In [1]:
import inspect
import sys
import os
from datetime import datetime
import pandas as pd
import time
from functools import reduce
import logging
from dateutil.relativedelta import relativedelta
from tables import NaturalNameWarning
import warnings
warnings.filterwarnings('ignore', category=NaturalNameWarning)
sys.path.insert(0, os.path.dirname(os.path.dirname(os.path.abspath(inspect.getfile(inspect.currentframe())))))
from swagger_client.api.default_api import DefaultApi
from configparser import ConfigParser
import smtplib
from email.message import EmailMessage
import shutil
import platform
import requests
from model.flight_result_model import *
import numpy as np
from sqlalchemy import create_engine
from sqlalchemy import Column, Integer, String
from sqlalchemy.ext.declarative import declarative_base
from sqlalchemy.orm import sessionmaker

In [67]:
np.round(11679.9999 / 395.377773,2)

29.54

In [65]:
!pip install schedule

  Using cached schedule-1.1.0-py2.py3-none-any.whl (10 kB)


In [2]:
def load_config():
    try:
        log.info("Config file load begin")
        config = ConfigParser()
        if platform.platform()[:platform.platform().index('-')].lower() == 'macos':
            config_path = '/Users/kuligabor/Documents/KIWI/flight_search_py_be/kiwi.cfg'
        else:
            config_path = '/data/flight/flight_search_py_be/kiwi.cfg'
        config.read(config_path, encoding='utf-8')
        log.info("Config file load end")
        return config

    except Exception as e:
        log.error("Config file load error: {}".format(str(e)))
        sys.exit(1)

def load_logger():

    try:
        log = logging.getLogger('LOG')
        log.setLevel(logging.DEBUG)
        fh = logging.FileHandler('fligh_runner.log', encoding="utf-8")
        fh.setLevel(logging.DEBUG)

        ch = logging.StreamHandler()
        ch.setLevel(logging.DEBUG)

        formatter = logging.Formatter('%(asctime)s - %(levelname)s - %(message)s', datefmt='%Y-%m-%d %H:%M:%S')
        ch.setFormatter(formatter)
        fh.setFormatter(formatter)

        log.addHandler(ch)
        log.addHandler(fh)
        log.info('Logger set')

        return log

    except Exception as e:
        print("logger error: " + str(e))
        sys.exit(1)

In [3]:
log = load_logger()
config = load_config()

'''date_from = config.get('BASE', "date_from")
date_to = config.get('BASE', "date_to")
nights_in_dst_from = config.get('BASE', "nights_in_dst_from")
nights_in_dst_to = config.get('BASE', "nights_in_dst_to")
max_stopovers = int(config.get('BASE', "max_stopovers"))
adults = int(config.get('BASE', "adults"))
children = int(config.get('BASE', "children"))
infants = int(config.get('BASE', "infants"))
adult_hold_bag = config.get('BASE', "adult_hold_bag")
adult_hand_bag = config.get('BASE', "adult_hand_bag")
child_hand_bag = config.get('BASE', "child_hand_bag")
airports = config.get('BASE', "airports")
h5_store_name = config.get('BASE', "h5_store_name")
h5_api_name = config.get('BASE', "h5_api_name")
result_dir = config.get('BASE', 'result_dir')
api_key = config.get('BASE', 'api_key')
'''

2023-03-16 11:14:23 - INFO - Logger set
2023-03-16 11:14:23 - INFO - Config file load begin
2023-03-16 11:14:23 - INFO - Config file load end


'date_from = config.get(\'BASE\', "date_from")\ndate_to = config.get(\'BASE\', "date_to")\nnights_in_dst_from = config.get(\'BASE\', "nights_in_dst_from")\nnights_in_dst_to = config.get(\'BASE\', "nights_in_dst_to")\nmax_stopovers = int(config.get(\'BASE\', "max_stopovers"))\nadults = int(config.get(\'BASE\', "adults"))\nchildren = int(config.get(\'BASE\', "children"))\ninfants = int(config.get(\'BASE\', "infants"))\nadult_hold_bag = config.get(\'BASE\', "adult_hold_bag")\nadult_hand_bag = config.get(\'BASE\', "adult_hand_bag")\nchild_hand_bag = config.get(\'BASE\', "child_hand_bag")\nairports = config.get(\'BASE\', "airports")\nh5_store_name = config.get(\'BASE\', "h5_store_name")\nh5_api_name = config.get(\'BASE\', "h5_api_name")\nresult_dir = config.get(\'BASE\', \'result_dir\')\napi_key = config.get(\'BASE\', \'api_key\')\n'

In [27]:
db_user = config.get('DB', "db_user")
db_pass = config.get('DB', "db_pass")
db_host = config.get('DB', "db_host")
db_port = config.get('DB', "db_port")
database= config.get('DB', "database")
connect_string = 'mysql+pymysql://' + db_user + ":" + db_pass + "@" + db_host + ":" + db_port + "/" + database

In [28]:
connection = create_engine(connect_string, pool_pre_ping=True, connect_args={'connect_timeout': 6000}).connect()

In [29]:
flight_req_sql = config.get('SQL', "flight_req_sql")

In [30]:
flight_req_df = pd.read_sql(flight_req_sql, connection)

In [31]:
flight_req_df

FSRE_ID       SEARCH_NAME DEP_AIRPORT   DATE_FROM     DATE_TO  \
0        5  ALL_EU_ONE_ADULT         BUD  01/04/2023  01/09/2023   

   NIGH_IN_DEST_FROM  NIGH_IN_DEST_TO  MAX_STOP_OVERS  ADULTS  CHILDREN  \
0                  2                3               0       1         0   

   INFANTS ADULT_HOLD_BAG ADULT_HAND_BAG CHILD_HAND_BAG  PRICE_LIMIT  \
0        0              0              0              0       100000   

              CR_DATE             MOD_DATE CR_USER  BOOL_ID  
0 2023-03-15 15:30:42  9999-12-31 00:00:00    None        1

In [40]:
fsin_4 = pd.read_sql('select * from FLIGHT_SEARCH_RESULT where FSIN_ID = 4', connection)
fsin_6 = pd.read_sql('select * from FLIGHT_SEARCH_RESULT where FSIN_ID = 6', connection)

In [43]:
len(fsin_4)

15464

In [44]:
len(fsin_6)

15156

In [45]:
fsin_4.drop_duplicates(subset=['ID'], inplace=True)
fsin_6.drop_duplicates(subset=['ID'], inplace=True)

In [46]:
len(fsin_4)

15040

In [47]:
len(fsin_6)

14742

In [48]:
fsin_4.to_sql('FLIGHT_SEARCH_RESULT', connection, if_exists='append', index=False)
fsin_6.to_sql('FLIGHT_SEARCH_RESULT', connection, if_exists='append', index=False)

14742

In [51]:
x = 'select re.*, group_concat(fda.IATA) IATA from FLIGHT_SEARCH_REQUEST re join FLIGHT_REL_REQUEST_AIRPORT relair on re.FSRE_ID = relair.FSRE_ID left join FLIGHT_D_AIRPORT fda on relair.FLDA_ID = fda.FLDA_ID where re.BOOL_ID = 1'

In [52]:
df = pd.read_sql(x, connection)

In [53]:
df.head()

FSRE_ID       SEARCH_NAME DEP_AIRPORT   DATE_FROM     DATE_TO  \
0        5  ALL_EU_ONE_ADULT         BUD  01/04/2023  01/09/2023   

   NIGH_IN_DEST_FROM  NIGH_IN_DEST_TO  MAX_STOP_OVERS  ADULTS  CHILDREN  \
0                  2                3               0       1         0   

   INFANTS ADULT_HOLD_BAG ADULT_HAND_BAG CHILD_HAND_BAG  PRICE_LIMIT  \
0        0              0              0              0       100000   

              CR_DATE             MOD_DATE CR_USER  BOOL_ID  \
0 2023-03-15 15:30:42  9999-12-31 00:00:00    None        1   

                                                IATA  
0  SJJ,SOF,BUD,SKP,BUH,OTP,EVN,BAK,MSQ,OMO,BOJ,GO...

In [64]:
df['IATA'].values[0].split(',')

['SJJ',
 'SOF',
 'BUD',
 'SKP',
 'BUH',
 'OTP',
 'EVN',
 'BAK',
 'MSQ',
 'OMO',
 'BOJ',
 'GOZ',
 'ROU',
 'SLS',
 'TGV',
 'VAR',
 'VID',
 'DBV',
 'LSZ',
 'OSI',
 'PUY',
 'RJK',
 'SPU',
 'ZAD',
 'ZAG',
 'QUF',
 'TLL',
 'TBS',
 'RIX',
 'VNO',
 'OHD',
 'CND',
 'AER',
 'KHV',
 'HTA',
 'IKT',
 'KZN',
 'MRV',
 'MOW',
 'DME',
 'SVO',
 'VKO',
 'MMK',
 'OVB',
 'LED',
 'UUD',
 'VLU',
 'ARH',
 'YKS',
 'BTS',
 'LJU',
 'MBX',
 'KBP',
 'IEV',
 'LWO',
 'NLV',
 'ODS',
 'SIP',
 'BEG',
 'INI',
 'QND',
 'TGD',
 'PRN',
 'TIV',
 'TIA',
 'INN',
 'SZG',
 'VIE',
 'CPH',
 'HEL',
 'BER',
 'SXF',
 'TXL',
 'DRS',
 'HAM',
 'ATH',
 'HEW',
 'CFU',
 'KGS',
 'JMK',
 'MJT',
 'RHO',
 'SKG',
 'IBZ',
 'ORK',
 'DUB',
 'GWY',
 'KIR',
 'NOC',
 'SNN',
 'CAG',
 'MLA',
 'BGO',
 'OSL',
 'TRF',
 'KRK',
 'WAW',
 'LIS',
 'PDL',
 'PMI',
 'SVQ',
 'VLC',
 'GOT',
 'STO',
 'ARN',
 'BMA',
 'BHD',
 'BFS',
 'PIK',
 'GLA',
 'INV',
 'ALV',
 'GRZ',
 'KLU',
 'LNZ',
 'ANR',
 'BRU',
 'LGG',
 'AKT',
 'LCA',
 'QLI',
 'NIC',
 'PFO',
 'PRG',
 'AAR',


In [38]:
df_tst.head()

FLSR_ID  FSIN_ID                                                 ID  PRICE  \
0    46270        6  0b7714fd4c4c0000933713ac_0|14fd0b774c4f0000360...  14122   
1    46271        6  0b7714fd4c3c000082377037_0|14fd0b774c3e0000390...  14410   
2    46272        6  0b77091e4c17000069dbe2a8_0|091e0b774c190000df4...  14781   
3    46273        6  0b77091e4c17000069dbe2a8_0|091e0b774c190000df4...  14781   
4    46274        6  0b7714fd4c3b000075dd9b3f_0|14fd0b774c3e0000390...  15212   

   FLY_DURATION  RET_DURATION  TOTAL_DURATION                      ID_OUT  \
0          1.25          1.25            2.50  0b7714fd4c4c0000933713ac_0   
1          1.25          1.25            2.50  0b7714fd4c3c000082377037_0   
2          2.17          2.00            4.17  0b77091e4c17000069dbe2a8_0   
3          2.17          2.00            4.17  0b77091e4c17000069dbe2a8_0   
4          1.25          1.25            2.50  0b7714fd4c3b000075dd9b3f_0   

         DEP_DATE_OUT        ARR_DATE_OUT  ...                     ID_BACK  \
0 2023-06-24 07:35:00 2023-06-24 08:50:00  ...  14fd0b774c4f00003608b3bd_0   
1 2023-06-08 12:00:00 2023-06-08 13:15:00  ...  14fd0b774c3e0000390e70d1_0   
2 2023-05-02 06:15:00 2023-05-02 08:25:00  ...  091e0b774c190000df45d162_0   
3 2023-05-02 06:15:00 2023-05-02 08:25:00  ...  091e0b774c190000df45d162_0   
4 2023-06-07 08:20:00 2023-06-07 09:35:00  ...  14fd0b774c3e0000390e70d1_0   

        DEP_DATE_BACK       ARR_DATE_BACK AIRLINE_BACK COUNTRY_FROM_BACK  \
0 2023-06-27 18:35:00 2023-06-27 19:50:00           FR           Hungary   
1 2023-06-10 05:55:00 2023-06-10 07:10:00           FR           Hungary   
2 2023-05-04 14:55:00 2023-05-04 16:55:00           W6           Hungary   
3 2023-05-04 14:55:00 2023-05-04 16:55:00           W6           Hungary   
4 2023-06-10 05:55:00 2023-06-10 07:10:00           FR           Hungary   

  COUNTRY_TO_BACK CITY_FROM_BACK CITY_TO_BACK FLIGHT_NO_BACK CR_DATE  
0          Poland         Poznań     Budapest           4272    None  
1          Poland         Poznań     Budapest           4272    None  
2         Belgium       Brussels     Budapest           2282    None  
3         Belgium       Brussels     Budapest           2282    None  
4          Poland         Poznań     Budapest           4272    None  

[5 rows x 26 columns]

In [39]:
len(df_tst)

15156

In [35]:
df_tst.drop_duplicates(subset=['ID'], inplace=True)

In [33]:
for k,v in flight_req_df.iterrows():
    airport_list_sql = config.get('SQL', "airport_list_sql").format(fsre_id=v['FSRE_ID'])
    airport_list_df = pd.read_sql(airport_list_sql, connection)

In [36]:
list(airport_list_df['IATA'])

['TIA',
 'EVN',
 'GRZ',
 'INN',
 'KLU',
 'LNZ',
 'SZG',
 'VIE',
 'GYD',
 'MSQ',
 'ANR',
 'BRU',
 'CRL',
 'LGG',
 'OST',
 'SJJ',
 'TZL',
 'BOJ',
 'SOF',
 'VAR',
 'DBV',
 'PUY',
 'SPU',
 'ZAD',
 'ZAG',
 'LCA',
 'PFO',
 'BRQ',
 'PRG',
 'AAL',
 'AAR',
 'BLL',
 'CPH',
 'FAE',
 'TLL',
 'HEL',
 'OUL',
 'RVN',
 'TMP',
 'TKU',
 'VAA',
 'AJA',
 'BIA',
 'EGC',
 'BIQ',
 'BOD',
 'BES',
 'FSC',
 'LIL',
 'LYS',
 'MRS',
 'MPL',
 'NTE',
 'NCE',
 'BVA',
 'CDG',
 'ORY',
 'SXB',
 'RNS',
 'RUN',
 'TLN',
 'TLS',
 'KUT',
 'TBS',
 'FMM',
 'BER',
 'SXF',
 'TXL',
 'BRE',
 'CGN',
 'DTM',
 'DRS',
 'DUS',
 'FRA',
 'HHN',
 'FDH',
 'HAM',
 'HAJ',
 'FKB',
 'LEJ',
 'MUC',
 'FMO',
 'NUE',
 'PAD',
 'STR',
 'NRN',
 'ATH',
 'CHQ',
 'CFU',
 'HER',
 'KGS',
 'JMK',
 'RHO',
 'JTR',
 'SKG',
 'ZTH',
 'BUD',
 'DEB',
 'KEF',
 'ORK',
 'DUB',
 'NOC',
 'KIR',
 'SNN',
 'AHO',
 'AOI',
 'BRI',
 'BGY',
 'BLQ',
 'BDS',
 'CAG',
 'CTA',
 'CIY',
 'FLR',
 'GOA',
 'SUF',
 'LIN',
 'MXP',
 'NAP',
 'OLB',
 'PMO',
 'PEG',
 'PSR',
 'PSA',
 'CIA',


In [47]:
def create_flight_search_instance(connection, fsre_id):
    
    class FlightSearchInstance(Base):
        __tablename__ = 'FLIGHT_SEARCH_INSTANCE'
        FSIN_ID = Column(Integer, primary_key=True)
        FSRE_ID = Column(Integer)
        
    Session = sessionmaker(bind=connection)
    session = Session()
    
    new_record = FlightSearchInstance(FSRE_ID=1)
    session.add(new_record)
    session.commit()
    
    return new_record.FSIN_ID

In [5]:
def get_data_from_api():

    log.info('get_data_from_api started!')

    api = DefaultApi()

    airports_list = airports.split(',')

    flight_result_list = []
    
    #log.debug(airports_list)

    for airport in airports_list:

        log.debug(f'Checking BUD to {airport}')

        base_url = f'https://api.tequila.kiwi.com/v2/search?fly_from=BUD&curr=HUF' \
                   f'&fly_to={airport}' \
                   f'&date_from={date_from}' \
                   f'&date_to={date_to}' \
                   f'&nights_in_dst_from={nights_in_dst_from}' \
                   f'&nights_in_dst_to={nights_in_dst_to}' \
                   f'&flight_type=round' \
                   f'&adults={adults}' \
                   f'&children={children}' \
                   f'&infants={infants}' \
                   f'&adult_hold_bag={adult_hold_bag}' \
                   f'&adult_hand_bag={adult_hand_bag}' \
                   f'&max_stopovers={max_stopovers}' \


        #log.info(base_url)

        r = requests.get(url=base_url, headers={"apikey": api_key})
        data = r.json()

        flight_result = FlightResultModel.from_dict(data)
        
        if (flight_result != None) & (len(flight_result.data)) > 0:
            
            result_list = []
    
            for data in flight_result.data:

                result_dict = {}

                result_dict['ID'] = data.id
                result_dict['PRICE'] = data.price
                result_dict['FLY_DURATION'] = np.round(int(data.duration.departure) / 3600, 2)
                result_dict['RET_DURATION'] = np.round(int(data.duration.duration_return) / 3600, 2) 
                result_dict['TOTAL_DURATION'] = np.round(int(data.duration.total) / 3600, 2)

                return_type = 0
                col_suffix = 'OUT'

                for route in data.route:

                    if return_type == 1:
                        col_suffix = 'BACK'

                    result_dict['ID_' + str(col_suffix)] = route.id
                    result_dict['DEP_DATE_' + str(col_suffix)] = route.local_departure
                    result_dict['ARR_DATE_' + str(col_suffix)] = route.local_arrival

                    result_dict['AIRLINE_' + str(col_suffix)] = route.airline
                    result_dict['CITY_FROM_' + str(col_suffix)] = route.city_from
                    result_dict['CITY_TO_' + str(col_suffix)] = route.city_to
                    result_dict['FLIGHT_NO_' + str(col_suffix)] = route.flight_no

                    return_type = return_type + 1


                result_list.append(result_dict)
                #log.debug(result_dict)
                
            df = pd.DataFrame(result_list)
            df['PRICE'] = df['PRICE'].astype(int)

            log.debug(f'Result dataframe len: {len(df)}')
            flight_result_list.append(df)
            
        else:
            
            log.debug('no routes found!')
            
    final_result = reduce(lambda left, right: pd.concat([left, right]), flight_result_list)
    final_result.sort_values('PRICE', inplace=True)
    final_result.reset_index(inplace=True, drop=True)
    final_result['DEP_DATE_OUT'] = final_result['DEP_DATE_OUT'].dt.strftime('%Y-%m-%d %H:%M')
    final_result['ARR_DATE_OUT'] = final_result['ARR_DATE_OUT'].dt.strftime('%Y-%m-%d %H:%M')
    final_result['DEP_DATE_BACK'] = final_result['DEP_DATE_BACK'].dt.strftime('%Y-%m-%d %H:%M')
    final_result['ARR_DATE_BACK'] = final_result['ARR_DATE_BACK'].dt.strftime('%Y-%m-%d %H:%M')
    
    return final_result

In [6]:
final_result = get_data_from_api()

2023-03-11 14:13:31 - INFO - get_data_from_api started!
2023-03-11 14:13:31 - DEBUG - Checking BUD to TIA
2023-03-11 14:13:33 - DEBUG - Result dataframe len: 59
2023-03-11 14:13:33 - DEBUG - Checking BUD to EVN
2023-03-11 14:13:33 - DEBUG - no routes found!
2023-03-11 14:13:33 - DEBUG - Checking BUD to GRZ
2023-03-11 14:13:35 - DEBUG - no routes found!
2023-03-11 14:13:35 - DEBUG - Checking BUD to INN
2023-03-11 14:13:36 - DEBUG - no routes found!
2023-03-11 14:13:36 - DEBUG - Checking BUD to KLU
2023-03-11 14:13:36 - DEBUG - no routes found!
2023-03-11 14:13:36 - DEBUG - Checking BUD to LNZ
2023-03-11 14:13:37 - DEBUG - no routes found!
2023-03-11 14:13:37 - DEBUG - Checking BUD to SZG
2023-03-11 14:13:39 - DEBUG - no routes found!
2023-03-11 14:13:39 - DEBUG - Checking BUD to VIE
2023-03-11 14:13:41 - DEBUG - no routes found!
2023-03-11 14:13:41 - DEBUG - Checking BUD to GYD
2023-03-11 14:13:43 - DEBUG - no routes found!
2023-03-11 14:13:43 - DEBUG - Checking BUD to MSQ
2023-03-11 14

2023-03-11 14:15:30 - DEBUG - no routes found!
2023-03-11 14:15:30 - DEBUG - Checking BUD to STR
2023-03-11 14:15:36 - DEBUG - no routes found!
2023-03-11 14:15:36 - DEBUG - Checking BUD to NRN
2023-03-11 14:15:36 - DEBUG - no routes found!
2023-03-11 14:15:36 - DEBUG - Checking BUD to ATH
2023-03-11 14:15:40 - DEBUG - no routes found!
2023-03-11 14:15:40 - DEBUG - Checking BUD to CHQ
2023-03-11 14:15:41 - DEBUG - Result dataframe len: 93
2023-03-11 14:15:41 - DEBUG - Checking BUD to CFU
2023-03-11 14:15:45 - DEBUG - no routes found!
2023-03-11 14:15:45 - DEBUG - Checking BUD to HER
2023-03-11 14:15:46 - DEBUG - no routes found!
2023-03-11 14:15:46 - DEBUG - Checking BUD to KGS
2023-03-11 14:15:47 - DEBUG - no routes found!
2023-03-11 14:15:47 - DEBUG - Checking BUD to JMK
2023-03-11 14:15:48 - DEBUG - no routes found!
2023-03-11 14:15:48 - DEBUG - Checking BUD to RHO
2023-03-11 14:15:50 - DEBUG - Result dataframe len: 93
2023-03-11 14:15:50 - DEBUG - Checking BUD to JTR
2023-03-11 14:

2023-03-11 14:17:47 - DEBUG - no routes found!
2023-03-11 14:17:47 - DEBUG - Checking BUD to LIS
2023-03-11 14:17:49 - DEBUG - no routes found!
2023-03-11 14:17:49 - DEBUG - Checking BUD to FNC
2023-03-11 14:17:51 - DEBUG - Result dataframe len: 59
2023-03-11 14:17:51 - DEBUG - Checking BUD to PDL
2023-03-11 14:17:52 - DEBUG - no routes found!
2023-03-11 14:17:52 - DEBUG - Checking BUD to OPO
2023-03-11 14:17:53 - DEBUG - Result dataframe len: 67
2023-03-11 14:17:53 - DEBUG - Checking BUD to OTP
2023-03-11 14:17:56 - DEBUG - Result dataframe len: 295
2023-03-11 14:17:56 - DEBUG - Checking BUD to CLJ
2023-03-11 14:17:57 - DEBUG - Result dataframe len: 55
2023-03-11 14:17:57 - DEBUG - Checking BUD to IAS
2023-03-11 14:17:59 - DEBUG - no routes found!
2023-03-11 14:17:59 - DEBUG - Checking BUD to TSR
2023-03-11 14:18:00 - DEBUG - no routes found!
2023-03-11 14:18:00 - DEBUG - Checking BUD to SVX
2023-03-11 14:18:01 - DEBUG - no routes found!
2023-03-11 14:18:01 - DEBUG - Checking BUD to K

2023-03-11 14:19:51 - DEBUG - no routes found!
2023-03-11 14:19:51 - DEBUG - Checking BUD to HUY
2023-03-11 14:19:52 - DEBUG - no routes found!
2023-03-11 14:19:52 - DEBUG - Checking BUD to JER
2023-03-11 14:19:53 - DEBUG - no routes found!
2023-03-11 14:19:53 - DEBUG - Checking BUD to LBA
2023-03-11 14:19:59 - DEBUG - Result dataframe len: 29
2023-03-11 14:19:59 - DEBUG - Checking BUD to LPL
2023-03-11 14:20:02 - DEBUG - no routes found!
2023-03-11 14:20:02 - DEBUG - Checking BUD to LCY
2023-03-11 14:20:04 - DEBUG - no routes found!
2023-03-11 14:20:04 - DEBUG - Checking BUD to LGW
2023-03-11 14:20:07 - DEBUG - no routes found!
2023-03-11 14:20:07 - DEBUG - Checking BUD to LHR
2023-03-11 14:20:11 - DEBUG - Result dataframe len: 243
2023-03-11 14:20:11 - DEBUG - Checking BUD to LTN
2023-03-11 14:20:15 - DEBUG - no routes found!
2023-03-11 14:20:15 - DEBUG - Checking BUD to SEN
2023-03-11 14:20:17 - DEBUG - no routes found!
2023-03-11 14:20:17 - DEBUG - Checking BUD to STN
2023-03-11 14

In [7]:
len(final_result)

5195

In [9]:
final_result.sort_values('PRICE', inplace=True)

In [10]:
final_result

ID   PRICE  FLY_DURATION  \
1417  0b7719be4c1000006844639b_0|19be0b774c140000cff...   15752          1.67   
3029  0b7723b04c0c0000a5657e1a_0|23b00b774c0f0000d49...   16360          1.33   
2365  0b7717594c1600009ae74c2c_0|17590b774c1a0000ffe...   16640          1.33   
2916  0b7714fd4c2d000048ad8121_0|14fd0b774c3000007d7...   16899          1.25   
1767  0b7718c54bf10000efd09189_0|18c50b774bf60000d8e...   16945          1.50   
...                                                 ...     ...           ...   
5191  0b770f644c004c0308f7030a_0|0b770f644c004c0308f...  245535          2.58   
1416  0b770eec4c9e0000a1d21311_0|0eec0b774ca10000494...  246174          2.25   
5193  0b770f644bf24bf6e51a02fe_0|0b770f644bf24bf6e51...  252443          2.58   
5192  0b770f644bf24bf6e277c6e7_0|0b770f644bf24bf6e27...  252443          2.58   
5194  0b770f644bf94bfc2cbeb03c_0|0b770f644bf94bfc2cb...  267886          2.58   

      RET_DURATION  TOTAL_DURATION                      ID_OUT  \
1417          1.67            3.33  0b7719be4c1000006844639b_0   
3029          1.33            2.67  0b7723b04c0c0000a5657e1a_0   
2365          1.33            2.67  0b7717594c1600009ae74c2c_0   
2916          1.25            2.50  0b7714fd4c2d000048ad8121_0   
1767          1.50            3.00  0b7718c54bf10000efd09189_0   
...            ...             ...                         ...   
5191          2.50            5.08  0b770f644c004c0308f7030a_0   
1416          2.33            4.58  0b770eec4c9e0000a1d21311_0   
5193          2.50            5.08  0b770f644bf24bf6e51a02fe_0   
5192          2.50            5.08  0b770f644bf24bf6e277c6e7_0   
5194          2.50            5.08  0b770f644bf94bfc2cbeb03c_0   

          DEP_DATE_OUT      ARR_DATE_OUT AIRLINE_OUT CITY_FROM_OUT  \
1417  2023-04-25 06:20  2023-04-25 09:00          W6      Budapest   
3029  2023-04-21 15:10  2023-04-21 16:30          FR      Budapest   
2365  2023-05-01 06:25  2023-05-01 07:45          W6      Budapest   
2916  2023-05-24 08:20  2023-05-24 09:35          FR      Budapest   
1767  2023-03-25 23:00  2023-03-26 00:30          FR      Budapest   
...                ...               ...         ...           ...   
5191  2023-04-09 21:05  2023-04-09 22:40          BA      Budapest   
1416  2023-09-14 14:30  2023-09-14 17:45          W6      Budapest   
5193  2023-03-26 21:05  2023-03-26 22:40          BA      Budapest   
5192  2023-03-26 21:05  2023-03-26 22:40          BA      Budapest   
5194  2023-04-02 21:05  2023-04-02 22:40          BA      Budapest   

       CITY_TO_OUT  FLIGHT_NO_OUT                     ID_BACK  \
1417  Thessaloniki           2447  19be0b774c140000cff6c89e_0   
3029        Warsaw           1923  23b00b774c0f0000d490e487_0   
2365     Podgorica           2231  17590b774c1a0000ffe0d01b_0   
2916        Poznań           4271  14fd0b774c3000007d747e24_0   
1767       Bologna           3827  18c50b774bf60000d8e040c2_0   
...            ...            ...                         ...   
5191        London            889  0b770f644c004c0308f7030a_1   
1416     Santorini           2453  0eec0b774ca10000494d93d4_0   
5193        London            889  0b770f644bf24bf6e51a02fe_1   
5192        London            889  0b770f644bf24bf6e277c6e7_1   
5194        London            889  0b770f644bf94bfc2cbeb03c_1   

         DEP_DATE_BACK     ARR_DATE_BACK AIRLINE_BACK CITY_FROM_BACK  \
1417  2023-04-29 09:45  2023-04-29 10:25           W6   Thessaloniki   
3029  2023-04-24 21:10  2023-04-24 22:30           FR         Warsaw   
2365  2023-05-05 14:10  2023-05-05 15:30           W6      Podgorica   
2916  2023-05-27 05:55  2023-05-27 07:10           FR         Poznań   
1767  2023-03-30 22:25  2023-03-30 23:55           FR        Bologna   
...                ...               ...          ...            ...   
5191  2023-04-12 14:00  2023-04-12 17:30           BA         London   
1416  2023-09-17 22:05  2023-09-17 23:25           W6      Santorini   
5193  2023-03-30 

In [11]:
final_result.columns

Index(['ID', 'PRICE', 'FLY_DURATION', 'RET_DURATION', 'TOTAL_DURATION',
       'ID_OUT', 'DEP_DATE_OUT', 'ARR_DATE_OUT', 'AIRLINE_OUT',
       'CITY_FROM_OUT', 'CITY_TO_OUT', 'FLIGHT_NO_OUT', 'ID_BACK',
       'DEP_DATE_BACK', 'ARR_DATE_BACK', 'AIRLINE_BACK', 'CITY_FROM_BACK',
       'CITY_TO_BACK', 'FLIGHT_NO_BACK'],
      dtype='object')

In [26]:
db_user = 'kebodev'
db_pass = 'SolarDhom1985+'
db_host = '95.138.193.102'
db_port = '3306'
database= 'flight'
connect_string = 'mysql+pymysql://' + db_user + ":" + db_pass + "@" + db_host + ":" + db_port + "/" + database

In [27]:
connection = create_engine(connect_string, pool_pre_ping=True, connect_args={'connect_timeout': 6000}).connect()

In [28]:
final_result.to_sql('FLIGHT_SEARCH_RESULT', connection, if_exists='append', index=False)

5195

In [29]:
x = 'TIA,EVN,GRZ,INN,KLU,LNZ,SZG,VIE,GYD,MSQ,ANR,BRU,CRL,LGG,OST,SJJ,TZL,BOJ,SOF,VAR,DBV,PUY,SPU,ZAD,ZAG,LCA,PFO,BRQ,PRG,AAL,AAR,BLL,CPH,FAE,TLL,HEL,OUL,RVN,TMP,TKU,VAA,AJA,BIA,EGC,BIQ,BOD,BES,FSC,LIL,LYS,MRS,MPL,NTE,NCE,BVA,CDG,ORY,SXB,RNS,RUN,TLN,TLS,KUT,TBS,FMM,BER,SXF,TXL,BRE,CGN,DTM,DRS,DUS,FRA,HHN,FDH,HAM,HAJ,FKB,LEJ,MUC,FMO,NUE,PAD,STR,NRN,ATH,CHQ,CFU,HER,KGS,JMK,RHO,JTR,SKG,ZTH,BUD,DEB,KEF,ORK,DUB,NOC,KIR,SNN,AHO,AOI,BRI,BGY,BLQ,BDS,CAG,CTA,CIY,FLR,GOA,SUF,LIN,MXP,NAP,OLB,PMO,PEG,PSR,PSA,CIA,FCO,TPS,TSF,TRN,VCE,VRN,ALA,TSE,PRN,RIX,KUN,VNO,LUX,MLA,KIV,TGD,TIV,AMS,EIN,GRQ,MST,RTM,SKP,AES,BGO,BOO,HAU,KRS,OSL,TRF,SVG,TOS,TRD,GDN,KTW,KRK,POZ,SZZ,WAW,WMI,WRO,FAO,LIS,FNC,PDL,OPO,OTP,CLJ,IAS,TSR,SVX,KRR,DME,SVO,VKO,ZIA,OVB,LED,AER,BEG,INI,BTS,KSC,LJU,ALC,LEI,OVD,BCN,BIO,FUE,GRO,LPA,GRX,IBZ,XRY,SPC,ACE,MAD,AGP,MAH,PMI,RMU,REU,SDR,SCQ,SVQ,TFN,TFS,VLC,ZAZ,GOT,MMX,ARN,BMA,NYO,VST,BSL,BRN,GVA,ZRH,ADA,ESB,AYT,DLM,IST,SAW,ADB,BJV,TZX,HRK,KBP,IEV,LWO,ODS,ABZ,BHD,BFS,BHX,BRS,CWL,DSA,EMA,EDI,EXT,GLA,PIK,HUY,JER,LBA,LPL,LCY,LGW,LHR,LTN,SEN,STN,MAN,NCL,SOU'

In [31]:
for x in x.split(','):
    print(x)

TIA
EVN
GRZ
INN
KLU
LNZ
SZG
VIE
GYD
MSQ
ANR
BRU
CRL
LGG
OST
SJJ
TZL
BOJ
SOF
VAR
DBV
PUY
SPU
ZAD
ZAG
LCA
PFO
BRQ
PRG
AAL
AAR
BLL
CPH
FAE
TLL
HEL
OUL
RVN
TMP
TKU
VAA
AJA
BIA
EGC
BIQ
BOD
BES
FSC
LIL
LYS
MRS
MPL
NTE
NCE
BVA
CDG
ORY
SXB
RNS
RUN
TLN
TLS
KUT
TBS
FMM
BER
SXF
TXL
BRE
CGN
DTM
DRS
DUS
FRA
HHN
FDH
HAM
HAJ
FKB
LEJ
MUC
FMO
NUE
PAD
STR
NRN
ATH
CHQ
CFU
HER
KGS
JMK
RHO
JTR
SKG
ZTH
BUD
DEB
KEF
ORK
DUB
NOC
KIR
SNN
AHO
AOI
BRI
BGY
BLQ
BDS
CAG
CTA
CIY
FLR
GOA
SUF
LIN
MXP
NAP
OLB
PMO
PEG
PSR
PSA
CIA
FCO
TPS
TSF
TRN
VCE
VRN
ALA
TSE
PRN
RIX
KUN
VNO
LUX
MLA
KIV
TGD
TIV
AMS
EIN
GRQ
MST
RTM
SKP
AES
BGO
BOO
HAU
KRS
OSL
TRF
SVG
TOS
TRD
GDN
KTW
KRK
POZ
SZZ
WAW
WMI
WRO
FAO
LIS
FNC
PDL
OPO
OTP
CLJ
IAS
TSR
SVX
KRR
DME
SVO
VKO
ZIA
OVB
LED
AER
BEG
INI
BTS
KSC
LJU
ALC
LEI
OVD
BCN
BIO
FUE
GRO
LPA
GRX
IBZ
XRY
SPC
ACE
MAD
AGP
MAH
PMI
RMU
REU
SDR
SCQ
SVQ
TFN
TFS
VLC
ZAZ
GOT
MMX
ARN
BMA
NYO
VST
BSL
BRN
GVA
ZRH
ADA
ESB
AYT
DLM
IST
SAW
ADB
BJV
TZX
HRK
KBP
IEV
LWO
ODS
ABZ
BHD
BFS
BHX
BRS
CWL
DSA
EMA
EDI
EXT
GLA


In [1]:
x = '{"search_id": "56bd9ab9-36cb-f3b8-d6c0-0caca2accc79", "currency": "HUF", "fx_rate": 382.006519, "data": [{"id": "0b770a224c4100007151a3a5_0|0a220b774c450000a94cee25_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 536.654031, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 146940.4926, "conversion": {"EUR": 384.654411, "HUF": 146940.4926}, "fare": {"adults": 73470.25, "children": 73470.25, "infants": 73470.25}, "bags_price": {"1": 71.75, "2": 143.318}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 2}, "airlines": ["FR"], "route": [{"id": "0b770a224c4100007151a3a5_0", "combination_id": "0b770a224c4100007151a3a5", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-13T10:15:00.000Z", "utc_arrival": "2023-06-13T08:15:00.000Z", "local_departure": "2023-06-13T06:55:00.000Z", "utc_departure": "2023-06-13T04:55:00.000Z"}, {"id": "0a220b774c450000a94cee25_0", "combination_id": "0a220b774c450000a94cee25", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-17T09:40:00.000Z", "utc_arrival": "2023-06-17T07:40:00.000Z", "local_departure": "2023-06-17T06:30:00.000Z", "utc_departure": "2023-06-17T04:30:00.000Z"}], "booking_token": "EVnOScMgHyLBheVyS7OngbDT5tAWJkHQKvyAZiHCxNQKLow1stgTpS6Pu1Zf-dHjYo8hyfBbIzsD4G-xL4TnUCXmPjoqRYX3nC_PgmlFY4nPLvV5kbbGAF4TvR0AfFBEmHxHC8xuYzOOnnQoRj_i1TIVr1W2wKxCowN5m7W3k9DQyUwvvvlx1ytdVzXqqq17oBOofCu0-jlnMuN8kEfKkyDVGR39WGs0CAQrYRCbCFHP2UkkLrxZ6z4-r--Sqf-1QQYEJmO4MHw64PpVZqnV6RzhywkYSh2A0Q9LMZ17ArY5fgwEqFYWZM3r6FeAjXCedpLev0sPGQbFFUTpY_73eiVPfThQCjxMAnUwtKM8TH9U_NqQiqLjcxOgBrA0vdDqkMozypVHFr4TLf-HcnJbVL_iwUM9TMeYkxw-0-3TPtt0Uk9vwrlgcCeqv6GIRu8Ex77wMMDANjeljVBIwuDJke7xAvYNc-vxQZAv1HwApdsX9Q4oFJkQ-_-huR3TQU_vq6SmGuqwTtPgJLLi_kXBL2a6fnmqqqmxyW_XmuaZL5nA2yaSajZQ4Rtvuc_JMa76xjc9H9Aamsh59HRZVK6bPDZAInBmJDJYI8FMPoLKhoSqSs5Btff5nGH6iQ8RFBYslCiIzHsWUwrnBr5-iWu1_8c0ugxqYKn-oA0QSC3H1EwVZ1kMxuAQ8KnoAPrc9X7R18Mzg-708tm_SPGTp3BQFCA==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c4100007151a3a5_0%7C0a220b774c450000a94cee25_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EVnOScMgHyLBheVyS7OngbDT5tAWJkHQKvyAZiHCxNQKLow1stgTpS6Pu1Zf-dHjYo8hyfBbIzsD4G-xL4TnUCXmPjoqRYX3nC_PgmlFY4nPLvV5kbbGAF4TvR0AfFBEmHxHC8xuYzOOnnQoRj_i1TIVr1W2wKxCowN5m7W3k9DQyUwvvvlx1ytdVzXqqq17oBOofCu0-jlnMuN8kEfKkyDVGR39WGs0CAQrYRCbCFHP2UkkLrxZ6z4-r--Sqf-1QQYEJmO4MHw64PpVZqnV6RzhywkYSh2A0Q9LMZ17ArY5fgwEqFYWZM3r6FeAjXCedpLev0sPGQbFFUTpY_73eiVPfThQCjxMAnUwtKM8TH9U_NqQiqLjcxOgBrA0vdDqkMozypVHFr4TLf-HcnJbVL_iwUM9TMeYkxw-0-3TPtt0Uk9vwrlgcCeqv6GIRu8Ex77wMMDANjeljVBIwuDJke7xAvYNc-vxQZAv1HwApdsX9Q4oFJkQ-_-huR3TQU_vq6SmGuqwTtPgJLLi_kXBL2a6fnmqqqmxyW_XmuaZL5nA2yaSajZQ4Rtvuc_JMa76xjc9H9Aamsh59HRZVK6bPDZAInBmJDJYI8FMPoLKhoSqSs5Btff5nGH6iQ8RFBYslCiIzHsWUwrnBr5-iWu1_8c0ugxqYKn-oA0QSC3H1EwVZ1kMxuAQ8KnoAPrc9X7R18Mzg-708tm_SPGTp3BQFCA==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-13T10:15:00.000Z", "utc_arrival": "2023-06-13T08:15:00.000Z", "local_departure": "2023-06-13T06:55:00.000Z", "utc_departure": "2023-06-13T04:55:00.000Z"}, {"id": "0b770a224c360000605964d6_0|0a220b774c390000ac91a717_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 549.966175, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 152025.8184, "conversion": {"EUR": 397.966555, "HUF": 152025.8184}, "fare": {"adults": 76012.91, "children": 76012.91, "infants": 76012.91}, "bags_price": {"1": 71.316, "2": 142.618}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 2}, "airlines": ["FR"], "route": [{"id": "0b770a224c360000605964d6_0", "combination_id": "0b770a224c360000605964d6", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-02T21:45:00.000Z", "utc_arrival": "2023-06-02T19:45:00.000Z", "local_departure": "2023-06-02T18:25:00.000Z", "utc_departure": "2023-06-02T16:25:00.000Z"}, {"id": "0a220b774c390000ac91a717_0", "combination_id": "0a220b774c390000ac91a717", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-05T10:15:00.000Z", "utc_arrival": "2023-06-05T08:15:00.000Z", "local_departure": "2023-06-05T07:05:00.000Z", "utc_departure": "2023-06-05T05:05:00.000Z"}], "booking_token": "EkTO1YgohXA5Ny7RstwPwJ5J_X69npB2V16Dwi8VLr50lAg9BY3Hy556YPTJgk0rnR9Y78T6dTrKINT01gCbHy-m4nDe1HQDplJxb2-F5JcBWRNEb1RL9lYq4HVPGiMaTfYk6wkYC07U-UvYucqSOpv3bx1Mqw0eraixcDwCUv7pvv3LcN_VxIXM_r817OWvy-Z_AdtiVoYl5jznydQgX6qWvgODZmNVhM5HVj6xrGUjTwe38Z03gAhSbKmwnFO6PXDzXb8v3neTf1QRooJu4OtBjHEX9PI8UZfQZWL_PiQJTI5ZuYoqOHkRxKVO5a0tefjAzwrnXa3l7jMnys35CEKviyCtnSGzVS7yPV_oKOWf6BChX99B0S_6BvXOKNIy9fpVlyxs75i2WQgfUlkwEExj8H29YhJusRfz0T1pWzVPXSkWrlYCweMNHFaBCAP9ZhFbLbL4knpscCZ7rRIl_o7TD4-MayGj1q9ikDL2tCP3TKy8evBK9Fe2MZpp7D2lWXKeJ9waZ2e5R0_ZadB44K0u91JXbdOtu25wL2ae3fO3LqKo24bN4aV2Jf8CxMnM2NZcVtrHqMANt4I_V6OccT_ClooolhWnb5PCmFkeDeaw9raStmj7PMsZzwEm4LqkBNK_QTDdnSx_jx_CaLVjnopYg_agVWcpwW6piN8bJyoUEhsJq4jMaW-J95Wqm-GA8jrT4QG5wKId-9arCXt9edGtw6BotH9f-wop2P7DhpmnOwM-XPF8eGMs5HdKj3FTecLV2wicuPR2VIqozRaGbIA==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c360000605964d6_0%7C0a220b774c390000ac91a717_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EkTO1YgohXA5Ny7RstwPwJ5J_X69npB2V16Dwi8VLr50lAg9BY3Hy556YPTJgk0rnR9Y78T6dTrKINT01gCbHy-m4nDe1HQDplJxb2-F5JcBWRNEb1RL9lYq4HVPGiMaTfYk6wkYC07U-UvYucqSOpv3bx1Mqw0eraixcDwCUv7pvv3LcN_VxIXM_r817OWvy-Z_AdtiVoYl5jznydQgX6qWvgODZmNVhM5HVj6xrGUjTwe38Z03gAhSbKmwnFO6PXDzXb8v3neTf1QRooJu4OtBjHEX9PI8UZfQZWL_PiQJTI5ZuYoqOHkRxKVO5a0tefjAzwrnXa3l7jMnys35CEKviyCtnSGzVS7yPV_oKOWf6BChX99B0S_6BvXOKNIy9fpVlyxs75i2WQgfUlkwEExj8H29YhJusRfz0T1pWzVPXSkWrlYCweMNHFaBCAP9ZhFbLbL4knpscCZ7rRIl_o7TD4-MayGj1q9ikDL2tCP3TKy8evBK9Fe2MZpp7D2lWXKeJ9waZ2e5R0_ZadB44K0u91JXbdOtu25wL2ae3fO3LqKo24bN4aV2Jf8CxMnM2NZcVtrHqMANt4I_V6OccT_ClooolhWnb5PCmFkeDeaw9raStmj7PMsZzwEm4LqkBNK_QTDdnSx_jx_CaLVjnopYg_agVWcpwW6piN8bJyoUEhsJq4jMaW-J95Wqm-GA8jrT4QG5wKId-9arCXt9edGtw6BotH9f-wop2P7DhpmnOwM-XPF8eGMs5HdKj3FTecLV2wicuPR2VIqozRaGbIA==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-02T21:45:00.000Z", "utc_arrival": "2023-06-02T19:45:00.000Z", "local_departure": "2023-06-02T18:25:00.000Z", "utc_departure": "2023-06-02T16:25:00.000Z"}, {"id": "0b770a224c450000d9d313ec_0|0a220b774c4800001d928f51_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 552.868019, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 153134.3417, "conversion": {"EUR": 400.868399, "HUF": 153134.3417}, "fare": {"adults": 76567.17, "children": 79465.65, "infants": 79465.65}, "bags_price": {"1": 87.752, "2": 183.106}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 6}, "airlines": ["FR"], "route": [{"id": "0b770a224c450000d9d313ec_0", "combination_id": "0b770a224c450000d9d313ec", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-17T13:25:00.000Z", "utc_arrival": "2023-06-17T11:25:00.000Z", "local_departure": "2023-06-17T10:05:00.000Z", "utc_departure": "2023-06-17T08:05:00.000Z"}, {"id": "0a220b774c4800001d928f51_0", "combination_id": "0a220b774c4800001d928f51", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-20T14:05:00.000Z", "utc_arrival": "2023-06-20T12:05:00.000Z", "local_departure": "2023-06-20T10:55:00.000Z", "utc_departure": "2023-06-20T08:55:00.000Z"}], "booking_token": "Ecpk5F2Q_tpVW-ZRRuauYF2vrqGhuXlaw6R1xrLxZusvNh1viHE8Afo0-HxI0-2Ta6nPtlqudTzO-MIK59ssIAHrFoV120cLtmW8zLtuIHNN7bU99cPzCaiAJRtOr3HyRUEVkGOLMH1tdJ8cRwBGYlWDa3f-TU2JUerNzT9VZVGoacakeaNOWBHFLJuU1MraOnrJCe2msDyrim2d4TUNoCqs6gdk30wc_l0WIMUzX2LFuZMbMVl3MxPAx8wEkig3pEX42_oE8yL45ADARPyCP1e7yoVpHisoswxXEFbbUed839C6ux-9MGGOd2zBQhvX07ZSIegoToZiVFjIFxBcPtr93KaR3vQNRbCIMho53_dM72oIeZ8Z9pSBBZ7F94_9gkd338u2GZQxMh1vThLEVc5wDCqcJK6-kVBvWdSzFbDDzWP36v6q8AgUVVVkBiodPrRMX2hh8SRLcw8Y9DWhJhZg0x0-MFqC3yjba-DQFMc6-gZJfkH8SxjSmGffimwCf-ZmenVzGv5PdhnT9J0RzqbUcqNgpFFrZBGG_M-gGFrH20LS1KiI55oD6j-TAeZSdMA3ElgeH3PAk668OSJrkh1-COwgLturlidTqikkOaFvU13DEqjLkWG1iWcyHd_6JQpJ3lcmd0X31Cu1vZaEPiIUbdUsihrKsGipZ6xaESF8vDuM6dZ73ruKulb_oaFbYXQgm0Ga6MOZHaC_2GnpfLLdXOOZOt1kNhx1Nm_M3iKI=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c450000d9d313ec_0%7C0a220b774c4800001d928f51_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=Ecpk5F2Q_tpVW-ZRRuauYF2vrqGhuXlaw6R1xrLxZusvNh1viHE8Afo0-HxI0-2Ta6nPtlqudTzO-MIK59ssIAHrFoV120cLtmW8zLtuIHNN7bU99cPzCaiAJRtOr3HyRUEVkGOLMH1tdJ8cRwBGYlWDa3f-TU2JUerNzT9VZVGoacakeaNOWBHFLJuU1MraOnrJCe2msDyrim2d4TUNoCqs6gdk30wc_l0WIMUzX2LFuZMbMVl3MxPAx8wEkig3pEX42_oE8yL45ADARPyCP1e7yoVpHisoswxXEFbbUed839C6ux-9MGGOd2zBQhvX07ZSIegoToZiVFjIFxBcPtr93KaR3vQNRbCIMho53_dM72oIeZ8Z9pSBBZ7F94_9gkd338u2GZQxMh1vThLEVc5wDCqcJK6-kVBvWdSzFbDDzWP36v6q8AgUVVVkBiodPrRMX2hh8SRLcw8Y9DWhJhZg0x0-MFqC3yjba-DQFMc6-gZJfkH8SxjSmGffimwCf-ZmenVzGv5PdhnT9J0RzqbUcqNgpFFrZBGG_M-gGFrH20LS1KiI55oD6j-TAeZSdMA3ElgeH3PAk668OSJrkh1-COwgLturlidTqikkOaFvU13DEqjLkWG1iWcyHd_6JQpJ3lcmd0X31Cu1vZaEPiIUbdUsihrKsGipZ6xaESF8vDuM6dZ73ruKulb_oaFbYXQgm0Ga6MOZHaC_2GnpfLLdXOOZOt1kNhx1Nm_M3iKI=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-17T13:25:00.000Z", "utc_arrival": "2023-06-17T11:25:00.000Z", "local_departure": "2023-06-17T10:05:00.000Z", "utc_departure": "2023-06-17T08:05:00.000Z"}, {"id": "0b770a224c43000004103d82_0|0a220b774c4700009310bb78_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 566.024305, "distance": 1975.87, "duration": {"departure": 11700, "return": 11400, "total": 23100}, "price": 158669.4694, "conversion": {"EUR": 415.358015, "HUF": 158669.4694}, "fare": {"adults": 79334.73, "children": 79334.73, "infants": 79334.73}, "bags_price": {"1": 82.586, "2": 174.972}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 158, "hold_height": 52, "hold_length": 78, "hold_weight": 20, "hold_width": 28, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 3, "personal_item_width": 15}, "availability": {"seats": 2}, "airlines": ["FR", "IB"], "route": [{"id": "0b770a224c43000004103d82_0", "combination_id": "0b770a224c43000004103d82", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "IB", "flight_no": 3279, "operating_carrier": "IB", "operating_flight_no": "3279", "fare_basis": "ADNNAOB4", "fare_category": "M", "fare_classes": "A", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-15T18:50:00.000Z", "utc_arrival": "2023-06-15T16:50:00.000Z", "local_departure": "2023-06-15T15:35:00.000Z", "utc_departure": "2023-06-15T13:35:00.000Z"}, {"id": "0a220b774c4700009310bb78_0", "combination_id": "0a220b774c4700009310bb78", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-19T10:15:00.000Z", "utc_arrival": "2023-06-19T08:15:00.000Z", "local_departure": "2023-06-19T07:05:00.000Z", "utc_departure": "2023-06-19T05:05:00.000Z"}], "booking_token": "E4wbrOizOXsOsUD8uBSuumTxwWOT5-UQuRLmXigUaD4vvfp5xGid_Zk_Lzz4jlwpm1NVDu9YKr2llTTI_ZL7uA-BdKdx27rxSJUkZlo8MaRpwduGK0gCbdYouqarKJTrYJ3VmnGGlcL9QePTTSqnrECnw-RLBpT6UWsdjRCzHbJ9z0zbAMTBWO2JBaCH5njOsyWo4_m371RrzHh_BpDhc-XP0KkYxrGaubZoydELE41iZjiKP3zXR-Hwgp6kq1t9Cxu4s5JBW3pX8PtbYpry-pQM14JnNW3yIW3qd8NYqX5orV7R5LUaLnpiMjfCLuYbCUbTozMrgKYzApXBk4llGWJOE_QRv-fled8KmsmAu7ghQ3L1_Oc8dIHZGT6UOtZ6lv2MUuciNImsB0MdAgsBpWp_kJezMVkMFD5WtKq80PFc6clF2xuw-o_siuQBmVQXEhF0i8JMqUdRaOAmCje4UM08K1-X_e20bpNbbgt1WzrZDwwUJQ4ZppOmlMAFNOcXfkZsi1uTsDMs6yvdZQNIljHB-5tm-Gn3BTY4FIA5JhyiuVFnpAt05UXllGrxEje94-yxdL625NhI7-K05zPnalNnZwGUUV0jd_gyWMlnBxlwkO8yP5WRkBfTIDlvxA6ygnF0lTRVC6Q07DLXZfGvJGitvBJkKEqyqMQBZF4dOIFWZHK6N9P18zekwdH92WS4_JncjfbSZLhDZkcPcW92iCYOmtbPGwU0sElUwF1KVmVeV7zTK3B3i-xVT4uwfcbx1dj7tJg1EFE8QNAbmmixNVf7GNbEpU0KibsfPRx5YRGw=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c43000004103d82_0%7C0a220b774c4700009310bb78_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=E4wbrOizOXsOsUD8uBSuumTxwWOT5-UQuRLmXigUaD4vvfp5xGid_Zk_Lzz4jlwpm1NVDu9YKr2llTTI_ZL7uA-BdKdx27rxSJUkZlo8MaRpwduGK0gCbdYouqarKJTrYJ3VmnGGlcL9QePTTSqnrECnw-RLBpT6UWsdjRCzHbJ9z0zbAMTBWO2JBaCH5njOsyWo4_m371RrzHh_BpDhc-XP0KkYxrGaubZoydELE41iZjiKP3zXR-Hwgp6kq1t9Cxu4s5JBW3pX8PtbYpry-pQM14JnNW3yIW3qd8NYqX5orV7R5LUaLnpiMjfCLuYbCUbTozMrgKYzApXBk4llGWJOE_QRv-fled8KmsmAu7ghQ3L1_Oc8dIHZGT6UOtZ6lv2MUuciNImsB0MdAgsBpWp_kJezMVkMFD5WtKq80PFc6clF2xuw-o_siuQBmVQXEhF0i8JMqUdRaOAmCje4UM08K1-X_e20bpNbbgt1WzrZDwwUJQ4ZppOmlMAFNOcXfkZsi1uTsDMs6yvdZQNIljHB-5tm-Gn3BTY4FIA5JhyiuVFnpAt05UXllGrxEje94-yxdL625NhI7-K05zPnalNnZwGUUV0jd_gyWMlnBxlwkO8yP5WRkBfTIDlvxA6ygnF0lTRVC6Q07DLXZfGvJGitvBJkKEqyqMQBZF4dOIFWZHK6N9P18zekwdH92WS4_JncjfbSZLhDZkcPcW92iCYOmtbPGwU0sElUwF1KVmVeV7zTK3B3i-xVT4uwfcbx1dj7tJg1EFE8QNAbmmixNVf7GNbEpU0KibsfPRx5YRGw=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-15T18:50:00.000Z", "utc_arrival": "2023-06-15T16:50:00.000Z", "local_departure": "2023-06-15T15:35:00.000Z", "utc_departure": "2023-06-15T13:35:00.000Z"}, {"id": "0b770a224c4800006d0d7298_0|0a220b774c4c0000b6fa7a34_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 569.455026, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 159470.6865, "conversion": {"EUR": 417.455406, "HUF": 159470.6865}, "fare": {"adults": 79735.34, "children": 79735.34, "infants": 79735.34}, "bags_price": {"1": 75.194, "2": 150.402}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 3}, "airlines": ["FR"], "route": [{"id": "0b770a224c4800006d0d7298_0", "combination_id": "0b770a224c4800006d0d7298", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-20T10:15:00.000Z", "utc_arrival": "2023-06-20T08:15:00.000Z", "local_departure": "2023-06-20T06:55:00.000Z", "utc_departure": "2023-06-20T04:55:00.000Z"}, {"id": "0a220b774c4c0000b6fa7a34_0", "combination_id": "0a220b774c4c0000b6fa7a34", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-24T09:40:00.000Z", "utc_arrival": "2023-06-24T07:40:00.000Z", "local_departure": "2023-06-24T06:30:00.000Z", "utc_departure": "2023-06-24T04:30:00.000Z"}], "booking_token": "Ey7I1fV1QbltYGtzjhHZ-3N9sOEy4sa2LIpxWptSE0ICS5jC2tJtgCWNXNQA7c967_8rX-KSyQAVVNApJm4EWz3OUArBl0FqBTt9qvgW4gvwOZyGfTktJZKhAHVgAAzacIp3W7g6OfqaBNU9QQ3PDR-80-HxAi4ErzqeRKcCRYEM5Q5Tvo1YwgXi9lznfv3D7tzxhpuWuSi-Rx0L9KgnMadQgXRlEsoLChzD8ARWUAPpbnS_ullOjAwaOFtYskAJP59Cy86LO44OwDjQAM2EavObr9Ml5Sh3Fai9lFO4EGTEBxyKlXw2P1edPZ2VVT9ZJYCnuAUcP1a-a0eAs11KzN5W_jzREh3UuN0c0LhJIlxXA506Ld0YuaviAWmY15Jtn_5oNKTEhhZVVIKWqDuImFNbct-1HdtH8qHjNol3q6nu3cS0TGVUP8s4hpuZthHyYTTafdXSMAvfZ6oBu2QLrSeZyYA52rzw88x_XV1fEFYqKZjYSuqvZAciT5Uq3kM_VqBUckZdf8QUHAFV-_ELDheMpaQZmf8bEEsgg67kl1AK1f88wlf6dGsmmYive4xGmgRKAYagb1slnBA1UqE1ZUD3zeI4oEpfV5Vz1xYMSu76eN0WDMJfyZEjHvlZIVJtLnxf2OivxMl9gWUkxK04PFfflACkk3MKSNUPGguwsT-MsHD5v59voOERAwhStGWFMVtHIMmFWIQ2fwRyOXc0s0aeIHSf0lP-RQrJSBY9gx7bwAl-lmOMUwtvm2wNENdpboKdE_Fc6hWArGoDwgt0gwYmQP6gTx-4Aw7RxAX4zrIU=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c4800006d0d7298_0%7C0a220b774c4c0000b6fa7a34_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=Ey7I1fV1QbltYGtzjhHZ-3N9sOEy4sa2LIpxWptSE0ICS5jC2tJtgCWNXNQA7c967_8rX-KSyQAVVNApJm4EWz3OUArBl0FqBTt9qvgW4gvwOZyGfTktJZKhAHVgAAzacIp3W7g6OfqaBNU9QQ3PDR-80-HxAi4ErzqeRKcCRYEM5Q5Tvo1YwgXi9lznfv3D7tzxhpuWuSi-Rx0L9KgnMadQgXRlEsoLChzD8ARWUAPpbnS_ullOjAwaOFtYskAJP59Cy86LO44OwDjQAM2EavObr9Ml5Sh3Fai9lFO4EGTEBxyKlXw2P1edPZ2VVT9ZJYCnuAUcP1a-a0eAs11KzN5W_jzREh3UuN0c0LhJIlxXA506Ld0YuaviAWmY15Jtn_5oNKTEhhZVVIKWqDuImFNbct-1HdtH8qHjNol3q6nu3cS0TGVUP8s4hpuZthHyYTTafdXSMAvfZ6oBu2QLrSeZyYA52rzw88x_XV1fEFYqKZjYSuqvZAciT5Uq3kM_VqBUckZdf8QUHAFV-_ELDheMpaQZmf8bEEsgg67kl1AK1f88wlf6dGsmmYive4xGmgRKAYagb1slnBA1UqE1ZUD3zeI4oEpfV5Vz1xYMSu76eN0WDMJfyZEjHvlZIVJtLnxf2OivxMl9gWUkxK04PFfflACkk3MKSNUPGguwsT-MsHD5v59voOERAwhStGWFMVtHIMmFWIQ2fwRyOXc0s0aeIHSf0lP-RQrJSBY9gx7bwAl-lmOMUwtvm2wNENdpboKdE_Fc6hWArGoDwgt0gwYmQP6gTx-4Aw7RxAX4zrIU=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-20T10:15:00.000Z", "utc_arrival": "2023-06-20T08:15:00.000Z", "local_departure": "2023-06-20T06:55:00.000Z", "utc_departure": "2023-06-20T04:55:00.000Z"}, {"id": "0b770a224c440000087d9250_0|0a220b774c4700009310bb78_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 578.75638, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 163023.8643, "conversion": {"EUR": 426.75676, "HUF": 163023.8643}, "fare": {"adults": 81511.93, "children": 81511.93, "infants": 81511.93}, "bags_price": {"1": 84.252, "2": 168.504}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 2}, "airlines": ["FR"], "route": [{"id": "0b770a224c440000087d9250_0", "combination_id": "0b770a224c440000087d9250", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-16T21:45:00.000Z", "utc_arrival": "2023-06-16T19:45:00.000Z", "local_departure": "2023-06-16T18:25:00.000Z", "utc_departure": "2023-06-16T16:25:00.000Z"}, {"id": "0a220b774c4700009310bb78_0", "combination_id": "0a220b774c4700009310bb78", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-19T10:15:00.000Z", "utc_arrival": "2023-06-19T08:15:00.000Z", "local_departure": "2023-06-19T07:05:00.000Z", "utc_departure": "2023-06-19T05:05:00.000Z"}], "booking_token": "EsEH2sFEiLZJLeT95zdBA0Q5Lh1pLpAfmv7onU_eUwzOz_g5c7adQcddKxv1Tu60YURQ9PrIXpzqMMANRyGFmE6PVlqHERYldiA7Muu3KFdTakqd4oIVM8BSm_gFd_g7Z8hA_ZMDAJYTaTH8TLmI7T-1FDE64pWRdBwSXszTePj1r0veUUj2Tq6QMVyOX0ZzQzhlKhUtK1rBrIKUfxRPH41jmBtQBpug5k34koPJWCjf7QUY4dY7oJlQWuazsHa4yMwZ77uIjT-6vd6DpN7G45O2pKQF9IsWqhyvOuP05RB2nsoPalq1_1iY-C9-wqdY64hTu-lMrWOoTfV4iunlVX5qLYIpUTRrm3OKORXMw9ivlfRatAyO7c39rMifd2gXZHRMEytLFGVToDH-aT5FT0xl0kdIvoN1dGv6EhwBy6QXjEiTaPXHhWn8B4QSOiaADn-iD3o56EgmgLGVTYuMK2aC-NG18k2qfIDIoaCXmsBolNCdzLtl1qf6OEnjHIrAvr07Y5lPedaB_fKr8AGRKhPJJ9Z-vVm74-tuE7PYSJY2rpILJqVTfr6FkZmfDPWnoK4pjSHj0UrBIohQdMwAecHX26rX_rwwYWrpYtzYOsr6ELR2Q0sOL4rF8q5U16KWN02rfP7HM51W5MEzXji9eOO9-m091qS7nnFsxH8khDskr95-q3vjSVLORmmyxnuGDt69QJgohLOfKoMG0uvp2n0Xfbdt0uYkCSrwrRq7kdY-QCc3bTHgkUEKf5_no5-6TWAD3vM94zrPIbBEXi1WV-A==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c440000087d9250_0%7C0a220b774c4700009310bb78_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EsEH2sFEiLZJLeT95zdBA0Q5Lh1pLpAfmv7onU_eUwzOz_g5c7adQcddKxv1Tu60YURQ9PrIXpzqMMANRyGFmE6PVlqHERYldiA7Muu3KFdTakqd4oIVM8BSm_gFd_g7Z8hA_ZMDAJYTaTH8TLmI7T-1FDE64pWRdBwSXszTePj1r0veUUj2Tq6QMVyOX0ZzQzhlKhUtK1rBrIKUfxRPH41jmBtQBpug5k34koPJWCjf7QUY4dY7oJlQWuazsHa4yMwZ77uIjT-6vd6DpN7G45O2pKQF9IsWqhyvOuP05RB2nsoPalq1_1iY-C9-wqdY64hTu-lMrWOoTfV4iunlVX5qLYIpUTRrm3OKORXMw9ivlfRatAyO7c39rMifd2gXZHRMEytLFGVToDH-aT5FT0xl0kdIvoN1dGv6EhwBy6QXjEiTaPXHhWn8B4QSOiaADn-iD3o56EgmgLGVTYuMK2aC-NG18k2qfIDIoaCXmsBolNCdzLtl1qf6OEnjHIrAvr07Y5lPedaB_fKr8AGRKhPJJ9Z-vVm74-tuE7PYSJY2rpILJqVTfr6FkZmfDPWnoK4pjSHj0UrBIohQdMwAecHX26rX_rwwYWrpYtzYOsr6ELR2Q0sOL4rF8q5U16KWN02rfP7HM51W5MEzXji9eOO9-m091qS7nnFsxH8khDskr95-q3vjSVLORmmyxnuGDt69QJgohLOfKoMG0uvp2n0Xfbdt0uYkCSrwrRq7kdY-QCc3bTHgkUEKf5_no5-6TWAD3vM94zrPIbBEXi1WV-A==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-16T21:45:00.000Z", "utc_arrival": "2023-06-16T19:45:00.000Z", "local_departure": "2023-06-16T18:25:00.000Z", "utc_departure": "2023-06-16T16:25:00.000Z"}, {"id": "0b770a224c4b000059b2d558_0|0a220b774c4f0000a7608cfc_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 581.404074, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 164035.3007, "conversion": {"EUR": 429.404454, "HUF": 164035.3007}, "fare": {"adults": 82017.65, "children": 82017.65, "infants": 82017.65}, "bags_price": {"1": 79.114, "2": 158.228}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 3}, "airlines": ["FR"], "route": [{"id": "0b770a224c4b000059b2d558_0", "combination_id": "0b770a224c4b000059b2d558", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-23T21:45:00.000Z", "utc_arrival": "2023-06-23T19:45:00.000Z", "local_departure": "2023-06-23T18:25:00.000Z", "utc_departure": "2023-06-23T16:25:00.000Z"}, {"id": "0a220b774c4f0000a7608cfc_0", "combination_id": "0a220b774c4f0000a7608cfc", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-27T14:05:00.000Z", "utc_arrival": "2023-06-27T12:05:00.000Z", "local_departure": "2023-06-27T10:55:00.000Z", "utc_departure": "2023-06-27T08:55:00.000Z"}], "booking_token": "EALetkdJe1tZCDRN6zO7MshnX34mLBXPTyZR3uW4IZOI1meQm_fQ5vjC0ffqQx-8TLs2B5dDPdTmg9TGOjqdL4926fXM4GwdjjsuSPvXKp_2Us8uDQxeTBW6gFE8E4bgkEaBJHfxqR98J5PV-DbXio1A2G-_elaEk6IrWSiZCSCvZiizE0pCq2tw6wNY-4uBkbD5Px8QK7SmafZcOH8HigkEkq_WNlaL8-JC3-jpVbOSuFLQF2SS0Vwbg3KLamj8-XnMzzXy5kcDpP9HzrPFYYMrHunDYaqGLE73t1MeGJBR1FYFHmz8C7gYPRjqPxvq82qYri-xgUzOvEkrNle57i4l0K3bp7LqN9TePSl37QH6xrgJIB68uF0aJKs24_BxWKYwGJYQkCA1vwbHsWjneV0WgM-AbHfa60CPwXOWE1315z1Z87rvBSjXw3QclAE58GTETeOfE-KZlJOO2hBji9yVRboN36lO9QnEF1jkOda8MD-nAuaPDR_ItsBC5FcVBHJGTo3ke8iMWORYGLAYlVRHdZWcUXPaVvYEXg2NxksEkBlW-1QSN8BKoh4yzFXamkXo1WIJ9sFOFO9eSRM0COYEok3Cms1rZhVcyQ1xUp-ltrma4gGkJjlQe_ON-dpuZP8xzOiCodGNhrVMbysyPAkwmd-7PO0AFJQISORW8NY3B5tnAZ6DoPCjnTl5pwdDaU-_KWO5_qnFO4ETyoiBGKj8dVvH3pljnf_Wag38FeLIKTOqEUvxoSv2I9Dqo-ZyWhotD2z_aTPNDQVP8RHYFEA==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c4b000059b2d558_0%7C0a220b774c4f0000a7608cfc_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EALetkdJe1tZCDRN6zO7MshnX34mLBXPTyZR3uW4IZOI1meQm_fQ5vjC0ffqQx-8TLs2B5dDPdTmg9TGOjqdL4926fXM4GwdjjsuSPvXKp_2Us8uDQxeTBW6gFE8E4bgkEaBJHfxqR98J5PV-DbXio1A2G-_elaEk6IrWSiZCSCvZiizE0pCq2tw6wNY-4uBkbD5Px8QK7SmafZcOH8HigkEkq_WNlaL8-JC3-jpVbOSuFLQF2SS0Vwbg3KLamj8-XnMzzXy5kcDpP9HzrPFYYMrHunDYaqGLE73t1MeGJBR1FYFHmz8C7gYPRjqPxvq82qYri-xgUzOvEkrNle57i4l0K3bp7LqN9TePSl37QH6xrgJIB68uF0aJKs24_BxWKYwGJYQkCA1vwbHsWjneV0WgM-AbHfa60CPwXOWE1315z1Z87rvBSjXw3QclAE58GTETeOfE-KZlJOO2hBji9yVRboN36lO9QnEF1jkOda8MD-nAuaPDR_ItsBC5FcVBHJGTo3ke8iMWORYGLAYlVRHdZWcUXPaVvYEXg2NxksEkBlW-1QSN8BKoh4yzFXamkXo1WIJ9sFOFO9eSRM0COYEok3Cms1rZhVcyQ1xUp-ltrma4gGkJjlQe_ON-dpuZP8xzOiCodGNhrVMbysyPAkwmd-7PO0AFJQISORW8NY3B5tnAZ6DoPCjnTl5pwdDaU-_KWO5_qnFO4ETyoiBGKj8dVvH3pljnf_Wag38FeLIKTOqEUvxoSv2I9Dqo-ZyWhotD2z_aTPNDQVP8RHYFEA==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-23T21:45:00.000Z", "utc_arrival": "2023-06-23T19:45:00.000Z", "local_departure": "2023-06-23T18:25:00.000Z", "utc_departure": "2023-06-23T16:25:00.000Z"}, {"id": "0b770a224c3a0000c54ce2f2_0|0a220b774c3d000018fc23d3_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 595.597705, "distance": 1975.87, "duration": {"departure": 12000, "return": 12900, "total": 24900}, "price": 166910.6565, "conversion": {"EUR": 436.931435, "HUF": 166910.6565}, "fare": {"adults": 83455.33, "children": 83455.33, "infants": 83455.33}, "bags_price": {"1": 88.368, "2": 176.75}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 2}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224c3a0000c54ce2f2_0", "combination_id": "0b770a224c3a0000c54ce2f2", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-06T10:15:00.000Z", "utc_arrival": "2023-06-06T08:15:00.000Z", "local_departure": "2023-06-06T06:55:00.000Z", "utc_departure": "2023-06-06T04:55:00.000Z"}, {"id": "0a220b774c3d000018fc23d3_0", "combination_id": "0a220b774c3d000018fc23d3", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "JKREG", "fare_category": "M", "fare_classes": "J", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-10T01:05:00.000Z", "utc_arrival": "2023-06-09T23:05:00.000Z", "local_departure": "2023-06-09T21:30:00.000Z", "utc_departure": "2023-06-09T19:30:00.000Z"}], "booking_token": "EikzOHItJzq4P_PaHaauZxV28esl_MxA1lmO1M6h_8hNibRPRp-0H3eJWaBuXCdfCBs8pzFd1PL8uVO53xoDZMwgivt7LYUwSmSxZakvR3Qo8ZrVafz3ImXEaf6zBdDgTUQ5dQzydpNYPXl8RVI1L4yxeHesLdpI-mbQgTldF68CI4r3vtERl_wToIWX_Q1eHoHNYVUUvPxF6TwwWkAwzUq-yB96rOf9n1B-NySgqaqQcAmBA6aIP3towI67zHfWFOSvxKo-Y6aSP2oXC5RD9ZtenPGS74lhzDDw6eYVZDwWdX30JHmEacmzCZV7zreuy8esYHQY8EiwB_OD1AXmMCcrEzxecARZyB9HrzoXbcac-3qdhBtu30l8ufKnUdf1SdL1BhtwTqRhtYDib65BFN34ogimdTPRJzRFeCpT6Dx037ZiIzAiNmcM12y56oDET_H6rSR0Z-tYAMT0TEi2NndMWqWwT0zCkKlB1IXF4PaeP4oCuNQUaVnkda4wA-BIGyXSTnMRFgu5SUFM8Ws_FuFLNa_pYMn9eON9i6tEDkiwGsHQJViO6u41yjtMA0_WopNJA2stSQG6St_Eq9hdEMk23WOgrdHl0EWAU567E8O0LZL9xfLpQcbh_Hw8BCXjAaJ109pAOu9WKUsMaEvG-q3EDtbsb2G9JlEuNVh8gFeZd2pDyjQE7QvcyPbrQCIKf802EwACCn_VOPLM9mtEpXIyRATfebJebuxGvPThlKnW1BMs4_XElG0NYL7DkbmowMwMwYehBwp1tNCd54gEHlQ==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c3a0000c54ce2f2_0%7C0a220b774c3d000018fc23d3_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EikzOHItJzq4P_PaHaauZxV28esl_MxA1lmO1M6h_8hNibRPRp-0H3eJWaBuXCdfCBs8pzFd1PL8uVO53xoDZMwgivt7LYUwSmSxZakvR3Qo8ZrVafz3ImXEaf6zBdDgTUQ5dQzydpNYPXl8RVI1L4yxeHesLdpI-mbQgTldF68CI4r3vtERl_wToIWX_Q1eHoHNYVUUvPxF6TwwWkAwzUq-yB96rOf9n1B-NySgqaqQcAmBA6aIP3towI67zHfWFOSvxKo-Y6aSP2oXC5RD9ZtenPGS74lhzDDw6eYVZDwWdX30JHmEacmzCZV7zreuy8esYHQY8EiwB_OD1AXmMCcrEzxecARZyB9HrzoXbcac-3qdhBtu30l8ufKnUdf1SdL1BhtwTqRhtYDib65BFN34ogimdTPRJzRFeCpT6Dx037ZiIzAiNmcM12y56oDET_H6rSR0Z-tYAMT0TEi2NndMWqWwT0zCkKlB1IXF4PaeP4oCuNQUaVnkda4wA-BIGyXSTnMRFgu5SUFM8Ws_FuFLNa_pYMn9eON9i6tEDkiwGsHQJViO6u41yjtMA0_WopNJA2stSQG6St_Eq9hdEMk23WOgrdHl0EWAU567E8O0LZL9xfLpQcbh_Hw8BCXjAaJ109pAOu9WKUsMaEvG-q3EDtbsb2G9JlEuNVh8gFeZd2pDyjQE7QvcyPbrQCIKf802EwACCn_VOPLM9mtEpXIyRATfebJebuxGvPThlKnW1BMs4_XElG0NYL7DkbmowMwMwYehBwp1tNCd54gEHlQ==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-06T10:15:00.000Z", "utc_arrival": "2023-06-06T08:15:00.000Z", "local_departure": "2023-06-06T06:55:00.000Z", "utc_departure": "2023-06-06T04:55:00.000Z"}, {"id": "0b770a224c290000e8e2d43c_0|0a220b774c2c000089e7df3d_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 591.060187, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 167723.9988, "conversion": {"EUR": 439.060567, "HUF": 167723.9988}, "fare": {"adults": 83862, "children": 83862, "infants": 83862}, "bags_price": {"1": 71.75, "2": 143.486}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 3}, "airlines": ["FR"], "route": [{"id": "0b770a224c290000e8e2d43c_0", "combination_id": "0b770a224c290000e8e2d43c", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-20T13:25:00.000Z", "utc_arrival": "2023-05-20T11:25:00.000Z", "local_departure": "2023-05-20T10:05:00.000Z", "utc_departure": "2023-05-20T08:05:00.000Z"}, {"id": "0a220b774c2c000089e7df3d_0", "combination_id": "0a220b774c2c000089e7df3d", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-23T14:05:00.000Z", "utc_arrival": "2023-05-23T12:05:00.000Z", "local_departure": "2023-05-23T10:55:00.000Z", "utc_departure": "2023-05-23T08:55:00.000Z"}], "booking_token": "EyPN9Qha_ovyZBMVlhm2W6KjAiT6bN2_FKAnNw__bWkosuLqKSk5L_dTYJM2WbCN1ytOffefx0Lw0jn0JYAkU0gjS0JwS4QL_oZlzOX1r-MTOw5Jv0m6PHDEhChK1H0ZdjOnqx5t9I7xC2S0UmeT5YCqXgqOwOexOFwooVybao4iMcT4OCu4WIQYw00F0_4sxTX6OVUcKxzS_0fwfnn2cbxUIOfCb_G713Rd1v7ddlHUn5kqf-VMF8SOG0xZykw-lgVZ0CPT3J6XYycIpY0kduDrWaH03_VvtDugOFW7KTsbKPFGV2KKtuyDoCRbNQqO7NlkXL5rlFWsDOOelIvuFcrNpCxYx3p-N5_0uqrJo4Ad1wGasxkK6SWEKEdXH0d3oqLdlM59348tGVzNTMSOWTDYrhFWKEFoSwANn60aHHr_L8U6LJtr2c_ZM2BbYZn1OV1gTQqCtSYNcoM5-K8oVg90sF66_DPmWkthj69aMrsYpzz_BELhG1u4OfFNXAHJpuaWK-uajl-ZNZMqqbPqbEfsR-f-g0NISg5lpDxhx3W5qcGsbF0OsEBUQyVZOnMKF1hfxKxu9-PtNbawwPvI1Ze3X7EzEeO5DVU5yzES05dSJRKWzSdUeu9PlDj0VPrMDyww4BXDLjHKOfweiEJD0RTkGGth-O_6BJOZZa_g9hiPNnqJ92rTwe8NqabKxnhx8qeemRbc1OASxEYH65shwFbhXYycwtyosIX-ft0MaMA3c5nrgm_5Dj97ZB8AueY0fn8Zgg2lo4GoPp02MjCcWww==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c290000e8e2d43c_0%7C0a220b774c2c000089e7df3d_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EyPN9Qha_ovyZBMVlhm2W6KjAiT6bN2_FKAnNw__bWkosuLqKSk5L_dTYJM2WbCN1ytOffefx0Lw0jn0JYAkU0gjS0JwS4QL_oZlzOX1r-MTOw5Jv0m6PHDEhChK1H0ZdjOnqx5t9I7xC2S0UmeT5YCqXgqOwOexOFwooVybao4iMcT4OCu4WIQYw00F0_4sxTX6OVUcKxzS_0fwfnn2cbxUIOfCb_G713Rd1v7ddlHUn5kqf-VMF8SOG0xZykw-lgVZ0CPT3J6XYycIpY0kduDrWaH03_VvtDugOFW7KTsbKPFGV2KKtuyDoCRbNQqO7NlkXL5rlFWsDOOelIvuFcrNpCxYx3p-N5_0uqrJo4Ad1wGasxkK6SWEKEdXH0d3oqLdlM59348tGVzNTMSOWTDYrhFWKEFoSwANn60aHHr_L8U6LJtr2c_ZM2BbYZn1OV1gTQqCtSYNcoM5-K8oVg90sF66_DPmWkthj69aMrsYpzz_BELhG1u4OfFNXAHJpuaWK-uajl-ZNZMqqbPqbEfsR-f-g0NISg5lpDxhx3W5qcGsbF0OsEBUQyVZOnMKF1hfxKxu9-PtNbawwPvI1Ze3X7EzEeO5DVU5yzES05dSJRKWzSdUeu9PlDj0VPrMDyww4BXDLjHKOfweiEJD0RTkGGth-O_6BJOZZa_g9hiPNnqJ92rTwe8NqabKxnhx8qeemRbc1OASxEYH65shwFbhXYycwtyosIX-ft0MaMA3c5nrgm_5Dj97ZB8AueY0fn8Zgg2lo4GoPp02MjCcWww==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-20T13:25:00.000Z", "utc_arrival": "2023-05-20T11:25:00.000Z", "local_departure": "2023-05-20T10:05:00.000Z", "utc_departure": "2023-05-20T08:05:00.000Z"}, {"id": "0b770a224c4b000059b2d558_0|0a220b774c4e000024b82646_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 593.888154, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 168804.3007, "conversion": {"EUR": 441.888534, "HUF": 168804.3007}, "fare": {"adults": 84402.15, "children": 84402.15, "infants": 84402.15}, "bags_price": {"1": 79.114, "2": 158.228}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 3}, "airlines": ["FR"], "route": [{"id": "0b770a224c4b000059b2d558_0", "combination_id": "0b770a224c4b000059b2d558", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-23T21:45:00.000Z", "utc_arrival": "2023-06-23T19:45:00.000Z", "local_departure": "2023-06-23T18:25:00.000Z", "utc_departure": "2023-06-23T16:25:00.000Z"}, {"id": "0a220b774c4e000024b82646_0", "combination_id": "0a220b774c4e000024b82646", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-26T10:15:00.000Z", "utc_arrival": "2023-06-26T08:15:00.000Z", "local_departure": "2023-06-26T07:05:00.000Z", "utc_departure": "2023-06-26T05:05:00.000Z"}], "booking_token": "EqCMqR6i5_Y2OUtkzrl6ocGx_UOwkHD7eT2NMxLXhblhL9FvuGZs5VYyTRcH3pm2NoJpLv6dKfxiU7m0mB5KJxkVTgXjLJaMKTFOkPkGBbwRrLBlVNaAD0yng6e3wN6sDtUrCRGFci4aYAS2_JbEsPmQEAfpIMEwkQbBUGoOAtnfFraY_EcYiksIXXZvxkeKH2vjZEKSRd156AHPxgKcADPY_F-JpEi_hyd7QQFR2RH78v0BDaaIDYa-_xGianYvBr97PTG071fzqHKlgrCZ_Euoo2uL3GcJbq__BRUrDa3qg37Th5OjQssahrpKg8jId3vY0WEVGnOX4aGtFrXhGA1JpdSHGTUyGMtoV3sDYhYhKLJwLkfnVeA5VGsl22HYBf8qaqowYzTTbnfU0RP44MnTPdgPq23DTTPmjgj43OawUMjnhGGN8uCyzsO0e7z9jx1JWuNtDaRWZvmYr6XQHP17ldo-4CB7gl5qWPFto3445PrUWS02A1-MCXn20dsRM90AhU68gj1GuCFV-IJnWulnVgebBnq9Gq-DGgjAvt81vWruhqa_EP1bvfq_QuQSsMFDMeHPxvfycFZzJZLi8Tyx2OcQz-_CLomp1ZVwakiwpS9dn_IpyJWL0vTqn1h_JD1xbPGr9JtIHRFLDjfodF1xcHcnE04jWs6K4XJxPLzioVGEKCA43GaWBwWYU7B1FDhofKPhEOB6MV7aT5Wsyr7-p6R1xcaR1XYr6x5UnecY6gH6UtPwaPmD77T8JOR-lv9F8zF8FEU4717w-HsDiEg==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c4b000059b2d558_0%7C0a220b774c4e000024b82646_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EqCMqR6i5_Y2OUtkzrl6ocGx_UOwkHD7eT2NMxLXhblhL9FvuGZs5VYyTRcH3pm2NoJpLv6dKfxiU7m0mB5KJxkVTgXjLJaMKTFOkPkGBbwRrLBlVNaAD0yng6e3wN6sDtUrCRGFci4aYAS2_JbEsPmQEAfpIMEwkQbBUGoOAtnfFraY_EcYiksIXXZvxkeKH2vjZEKSRd156AHPxgKcADPY_F-JpEi_hyd7QQFR2RH78v0BDaaIDYa-_xGianYvBr97PTG071fzqHKlgrCZ_Euoo2uL3GcJbq__BRUrDa3qg37Th5OjQssahrpKg8jId3vY0WEVGnOX4aGtFrXhGA1JpdSHGTUyGMtoV3sDYhYhKLJwLkfnVeA5VGsl22HYBf8qaqowYzTTbnfU0RP44MnTPdgPq23DTTPmjgj43OawUMjnhGGN8uCyzsO0e7z9jx1JWuNtDaRWZvmYr6XQHP17ldo-4CB7gl5qWPFto3445PrUWS02A1-MCXn20dsRM90AhU68gj1GuCFV-IJnWulnVgebBnq9Gq-DGgjAvt81vWruhqa_EP1bvfq_QuQSsMFDMeHPxvfycFZzJZLi8Tyx2OcQz-_CLomp1ZVwakiwpS9dn_IpyJWL0vTqn1h_JD1xbPGr9JtIHRFLDjfodF1xcHcnE04jWs6K4XJxPLzioVGEKCA43GaWBwWYU7B1FDhofKPhEOB6MV7aT5Wsyr7-p6R1xcaR1XYr6x5UnecY6gH6UtPwaPmD77T8JOR-lv9F8zF8FEU4717w-HsDiEg==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-23T21:45:00.000Z", "utc_arrival": "2023-06-23T19:45:00.000Z", "local_departure": "2023-06-23T18:25:00.000Z", "utc_departure": "2023-06-23T16:25:00.000Z"}, {"id": "0b770a224c390000dc0e5ade_0|0a220b774c3d000018fc23d3_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 601.57666, "distance": 1975.87, "duration": {"departure": 12000, "return": 12900, "total": 24900}, "price": 169194.6563, "conversion": {"EUR": 442.91039, "HUF": 169194.6563}, "fare": {"adults": 84597.33, "children": 84597.33, "infants": 84597.33}, "bags_price": {"1": 88.368, "2": 176.75}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 2}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224c390000dc0e5ade_0", "combination_id": "0b770a224c390000dc0e5ade", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-05T14:00:00.000Z", "utc_arrival": "2023-06-05T12:00:00.000Z", "local_departure": "2023-06-05T10:40:00.000Z", "utc_departure": "2023-06-05T08:40:00.000Z"}, {"id": "0a220b774c3d000018fc23d3_0", "combination_id": "0a220b774c3d000018fc23d3", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "JKREG", "fare_category": "M", "fare_classes": "J", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-10T01:05:00.000Z", "utc_arrival": "2023-06-09T23:05:00.000Z", "local_departure": "2023-06-09T21:30:00.000Z", "utc_departure": "2023-06-09T19:30:00.000Z"}], "booking_token": "EE5ROjbKoAWjH2OuDy85iNcEGSsJPb_tE7iitXhmJYK0qEXyP7Bi3PXoRQnA_u2zoaX9VO1iO_blV4XRlGKWPD2Xg1dN2601FIUBnY_H0iu6bWDuxWjegwi6Q9g4uoitOxVW3XM52BBICL7o7gWkXXOebr7yX9sG3Y-SwNpLPAUuuOI8DpTHK8kTYxG6oX5Gqm7ut5XcIHdcMS0DhwLTXpQHsZKf0SpmhwUQBCV9ySFruJFcWAPSaQc9j-biShOh_U7Koq3RDt0faIlZsPw6HUqv14UrxOaz9Jnk3bBRl8MNKxUn0kC5VUpvskCmoy00OocxCQqWQXToDGOBik_ZxU4ZaOjHKoK_nLtcQ9qgkLOdck1YZWVZ_HD-dLpBts9PssLusU7hvPWpz0q6PuuqHgWTQaxWvI8Hd49TVjyVNRcG-5wQU9tE3HCpSgaVoRZEJpn1cv6TIOflMBuzHwXWasEceVLqqxfbMisuqCdoCC-1XWRDYe9XbA1QsWniPThr67RqzrT3FwMQB6x0hA9u6ALPQEkVcgb8R70Itq_VHHxXKcG7X6bQcbeTEdJ2PETa9ibSX3e8w2zwebWRbhJcqTen3wd8jAfuTAyT0q1RhAZV6Fji5w-wdsGmD4ENfq8uoTrExBdjlcXgV7gtjtwbU_fzfGAUuycmnvb7Cj4Sa6jucVb_o3VGCX56WiRuzinAxpH8DP-KaSFB1EC0nnzFSM1j8zELV4smkqfghF11yyuPG9qGLdu6i1iuUb1TcPVRi", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c390000dc0e5ade_0%7C0a220b774c3d000018fc23d3_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EE5ROjbKoAWjH2OuDy85iNcEGSsJPb_tE7iitXhmJYK0qEXyP7Bi3PXoRQnA_u2zoaX9VO1iO_blV4XRlGKWPD2Xg1dN2601FIUBnY_H0iu6bWDuxWjegwi6Q9g4uoitOxVW3XM52BBICL7o7gWkXXOebr7yX9sG3Y-SwNpLPAUuuOI8DpTHK8kTYxG6oX5Gqm7ut5XcIHdcMS0DhwLTXpQHsZKf0SpmhwUQBCV9ySFruJFcWAPSaQc9j-biShOh_U7Koq3RDt0faIlZsPw6HUqv14UrxOaz9Jnk3bBRl8MNKxUn0kC5VUpvskCmoy00OocxCQqWQXToDGOBik_ZxU4ZaOjHKoK_nLtcQ9qgkLOdck1YZWVZ_HD-dLpBts9PssLusU7hvPWpz0q6PuuqHgWTQaxWvI8Hd49TVjyVNRcG-5wQU9tE3HCpSgaVoRZEJpn1cv6TIOflMBuzHwXWasEceVLqqxfbMisuqCdoCC-1XWRDYe9XbA1QsWniPThr67RqzrT3FwMQB6x0hA9u6ALPQEkVcgb8R70Itq_VHHxXKcG7X6bQcbeTEdJ2PETa9ibSX3e8w2zwebWRbhJcqTen3wd8jAfuTAyT0q1RhAZV6Fji5w-wdsGmD4ENfq8uoTrExBdjlcXgV7gtjtwbU_fzfGAUuycmnvb7Cj4Sa6jucVb_o3VGCX56WiRuzinAxpH8DP-KaSFB1EC0nnzFSM1j8zELV4smkqfghF11yyuPG9qGLdu6i1iuUb1TcPVRi", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-05T14:00:00.000Z", "utc_arrival": "2023-06-05T12:00:00.000Z", "local_departure": "2023-06-05T10:40:00.000Z", "utc_departure": "2023-06-05T08:40:00.000Z"}, {"id": "0b770a224c3d0000866dbf36_0|0a220b774c40000011657e80_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 597.701254, "distance": 1975.87, "duration": {"departure": 12600, "return": 11400, "total": 24000}, "price": 169242.2482, "conversion": {"EUR": 443.034974, "HUF": 169242.2482}, "fare": {"adults": 84621.12, "children": 84621.12, "infants": 84621.12}, "bags_price": {"1": 93.086, "2": 186.172}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 3}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224c3d0000866dbf36_0", "combination_id": "0b770a224c3d0000866dbf36", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "KREG", "fare_category": "M", "fare_classes": "K", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-09T20:45:00.000Z", "utc_arrival": "2023-06-09T18:45:00.000Z", "local_departure": "2023-06-09T17:15:00.000Z", "utc_departure": "2023-06-09T15:15:00.000Z"}, {"id": "0a220b774c40000011657e80_0", "combination_id": "0a220b774c40000011657e80", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-12T10:15:00.000Z", "utc_arrival": "2023-06-12T08:15:00.000Z", "local_departure": "2023-06-12T07:05:00.000Z", "utc_departure": "2023-06-12T05:05:00.000Z"}], "booking_token": "E17T_jPjQY9IeZEsIEx694cJVAX7GZ4mK0S0mh9tAGdYwGI2kCF3ydl2H_KhjarR1_5Fnns7d_Y4oQd97m0VMbqd_xnilGj_QEB-qB-p4CxplQpv7FKFz_Vd6CoJLOXkgoXzRuaRlD7a4m_r1yZh9UClpJ_YoGTDzDiwmma39oYmUpj0wZfZR159tChspd-mNH1oa8HwjipvETSlTN4DuSvK7ftZH26tkXmur9iUzbt-9DWjc_CUGOA4xHYQhPrxL6ndjE9PFeI9G2jAFg48mDWogXxio_If2oZ0MYOE-mjBAPUgZOc67c3bX5fJrjOF_9sUw7Ob00Ra5XjzW_BEBoT7Uk76rnODRzj9Omlw9rNuUWtAfgNk55or4AWlH2zKXU7w06dr6JD9w9hYdovYyabSgVK7ULTbeOoeg7nzTRbzEeg4nDISJpg7k9ar2dmWuTHLidrfXYJWeOnP5h9rbUbaKpOBFTWHasuzIyu_gJH1aM7Ib8PU3lEQQzbpxXnnMcssxAagj-dfroTsW6aH11kdZm69rmWIc5Om6_iArIpZKiw-cq6xQBCfWWOC3VAEHlQinLUlpOApGOrPsR7V5NFcklfLG5J92TzNCSdcOAXljZZEtG7pHdpl_XpYvA2-CJ05CCjQtn8MII8KIAsIea0Pbl4_6M6UGTR8MwQvS71Y--D5wVzaYTVNJogML9cRzt7tTHH1nepTzDRLr8FinllI35v-WNSQpGFU9xNtfGMpfdF8XrjGTZrm4aTbcAYJ8OqVRl6kDCGXhZKqaS9gEx3C_QisPxgPhYxoC7s3Ov8Q=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c3d0000866dbf36_0%7C0a220b774c40000011657e80_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=E17T_jPjQY9IeZEsIEx694cJVAX7GZ4mK0S0mh9tAGdYwGI2kCF3ydl2H_KhjarR1_5Fnns7d_Y4oQd97m0VMbqd_xnilGj_QEB-qB-p4CxplQpv7FKFz_Vd6CoJLOXkgoXzRuaRlD7a4m_r1yZh9UClpJ_YoGTDzDiwmma39oYmUpj0wZfZR159tChspd-mNH1oa8HwjipvETSlTN4DuSvK7ftZH26tkXmur9iUzbt-9DWjc_CUGOA4xHYQhPrxL6ndjE9PFeI9G2jAFg48mDWogXxio_If2oZ0MYOE-mjBAPUgZOc67c3bX5fJrjOF_9sUw7Ob00Ra5XjzW_BEBoT7Uk76rnODRzj9Omlw9rNuUWtAfgNk55or4AWlH2zKXU7w06dr6JD9w9hYdovYyabSgVK7ULTbeOoeg7nzTRbzEeg4nDISJpg7k9ar2dmWuTHLidrfXYJWeOnP5h9rbUbaKpOBFTWHasuzIyu_gJH1aM7Ib8PU3lEQQzbpxXnnMcssxAagj-dfroTsW6aH11kdZm69rmWIc5Om6_iArIpZKiw-cq6xQBCfWWOC3VAEHlQinLUlpOApGOrPsR7V5NFcklfLG5J92TzNCSdcOAXljZZEtG7pHdpl_XpYvA2-CJ05CCjQtn8MII8KIAsIea0Pbl4_6M6UGTR8MwQvS71Y--D5wVzaYTVNJogML9cRzt7tTHH1nepTzDRLr8FinllI35v-WNSQpGFU9xNtfGMpfdF8XrjGTZrm4aTbcAYJ8OqVRl6kDCGXhZKqaS9gEx3C_QisPxgPhYxoC7s3Ov8Q=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-09T20:45:00.000Z", "utc_arrival": "2023-06-09T18:45:00.000Z", "local_departure": "2023-06-09T17:15:00.000Z", "utc_departure": "2023-06-09T15:15:00.000Z"}, {"id": "0b770a224c1e00003e2ba34c_0|0a220b774c21000064f4da0b_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 604.749377, "distance": 1975.87, "duration": {"departure": 12000, "return": 12900, "total": 24900}, "price": 170406.6549, "conversion": {"EUR": 446.083107, "HUF": 170406.6549}, "fare": {"adults": 85203.33, "children": 85203.33, "infants": 85203.33}, "bags_price": {"1": 84.882, "2": 169.764}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 2}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224c1e00003e2ba34c_0", "combination_id": "0b770a224c1e00003e2ba34c", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-09T10:15:00.000Z", "utc_arrival": "2023-05-09T08:15:00.000Z", "local_departure": "2023-05-09T06:55:00.000Z", "utc_departure": "2023-05-09T04:55:00.000Z"}, {"id": "0a220b774c21000064f4da0b_0", "combination_id": "0a220b774c21000064f4da0b", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "BOREG", "fare_category": "M", "fare_classes": "B", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-13T00:05:00.000Z", "utc_arrival": "2023-05-12T22:05:00.000Z", "local_departure": "2023-05-12T20:30:00.000Z", "utc_departure": "2023-05-12T18:30:00.000Z"}], "booking_token": "EV9oVusBEQdUZQbS5eKoil_ZXaN4fFd5qfPDKfmxexT-qqe-VIOcplg4pGYkgQEV32HMSOP9NM7VZhGss47-NcoJFKjN3AhkV1DPOZ5sBZcKHnIXd1qqVuHJxvBYHvqRWJOwW6X0C8D8kxc-ePgo8W8OlwsCpk_wAE40Y1OzujUa5SwB-EcY6_20NJsbiX9F_RAXYu2aFRFVlRlNN-4okASe4PDOCf2MQK-s5maJr2Bwy9t1Oad0JXu4e1mWpXFyUmRi7uI5DkF2tVMT0HbfFC5Se5LU-n5s8FEd_qRsz-P-URD3PtJmQSqWMcADt8bcYmMf2T6_xpx_7ecFvplU_gF41ByaEtyxmt-jXupiUg-fu-JFD3tOX7X2IlXbh0bXkASb18JQaRf42qEaTAspVgMIrFsMH69llleiDHYpV5SCMjr3R4Vy3EN03xUkOvRp2nmOgyJnXDLy_SakqZoxpAIFjfW9LiBFIUrCEFBIPaW2spquoOrg_q5BQjO1P9GwmeDc8sFLtQxHi5bzgVX2gGPUTLyjvpgcvb9Yj_14faJyYwIocSpGjESc2Tlad7JoL2KReDsRYIEQgYRJQBdJRnFv4SRdXNe1p5qFOQ1nQLjcL-orImFrC-6MexE9B4jHRD0cG05cYAn-e313-JIaRg0AIeJ58DASxpvLIaDBKyn41-0D3rHrvxtwJ7ntydjjGht9OPG9uCBB67vFdr6ppXxgHKLMME-eFVDAXipgzsHdhWg04bMjp0VUVVlwDqzyMJvqAiSIs09PWblFUWM1Daw==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c1e00003e2ba34c_0%7C0a220b774c21000064f4da0b_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EV9oVusBEQdUZQbS5eKoil_ZXaN4fFd5qfPDKfmxexT-qqe-VIOcplg4pGYkgQEV32HMSOP9NM7VZhGss47-NcoJFKjN3AhkV1DPOZ5sBZcKHnIXd1qqVuHJxvBYHvqRWJOwW6X0C8D8kxc-ePgo8W8OlwsCpk_wAE40Y1OzujUa5SwB-EcY6_20NJsbiX9F_RAXYu2aFRFVlRlNN-4okASe4PDOCf2MQK-s5maJr2Bwy9t1Oad0JXu4e1mWpXFyUmRi7uI5DkF2tVMT0HbfFC5Se5LU-n5s8FEd_qRsz-P-URD3PtJmQSqWMcADt8bcYmMf2T6_xpx_7ecFvplU_gF41ByaEtyxmt-jXupiUg-fu-JFD3tOX7X2IlXbh0bXkASb18JQaRf42qEaTAspVgMIrFsMH69llleiDHYpV5SCMjr3R4Vy3EN03xUkOvRp2nmOgyJnXDLy_SakqZoxpAIFjfW9LiBFIUrCEFBIPaW2spquoOrg_q5BQjO1P9GwmeDc8sFLtQxHi5bzgVX2gGPUTLyjvpgcvb9Yj_14faJyYwIocSpGjESc2Tlad7JoL2KReDsRYIEQgYRJQBdJRnFv4SRdXNe1p5qFOQ1nQLjcL-orImFrC-6MexE9B4jHRD0cG05cYAn-e313-JIaRg0AIeJ58DASxpvLIaDBKyn41-0D3rHrvxtwJ7ntydjjGht9OPG9uCBB67vFdr6ppXxgHKLMME-eFVDAXipgzsHdhWg04bMjp0VUVVlwDqzyMJvqAiSIs09PWblFUWM1Daw==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-09T10:15:00.000Z", "utc_arrival": "2023-05-09T08:15:00.000Z", "local_departure": "2023-05-09T06:55:00.000Z", "utc_departure": "2023-05-09T04:55:00.000Z"}, {"id": "0b770a224c3d000092cf2d05_0|0a220b774c40000011657e80_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 600.432131, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 171304.1425, "conversion": {"EUR": 448.432511, "HUF": 171304.1425}, "fare": {"adults": 85652.07, "children": 85652.07, "infants": 85652.07}, "bags_price": {"1": 70.672, "2": 141.372}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 6}, "airlines": ["FR"], "route": [{"id": "0b770a224c3d000092cf2d05_0", "combination_id": "0b770a224c3d000092cf2d05", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-09T21:45:00.000Z", "utc_arrival": "2023-06-09T19:45:00.000Z", "local_departure": "2023-06-09T18:25:00.000Z", "utc_departure": "2023-06-09T16:25:00.000Z"}, {"id": "0a220b774c40000011657e80_0", "combination_id": "0a220b774c40000011657e80", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-12T10:15:00.000Z", "utc_arrival": "2023-06-12T08:15:00.000Z", "local_departure": "2023-06-12T07:05:00.000Z", "utc_departure": "2023-06-12T05:05:00.000Z"}], "booking_token": "EEF-z33U0bXO_BiIG8zNGmNEI0x7xnBb1yaNvXJ5ptySU4ks1gAzDLP2B2koOP27O27TsFzvmGWFpcCSpi75z-SGpUw1-iKf1XuJre1LBnuTjr_eyJuBzgQTid6aqtQtaL84I_Pqbi2BJoNcd_fLjDjzFyKCss_v29GkFRCjhAIGuZf3DMQxmFfUzGyNvstkGNpmdDJIKXOCE9tADbfgqA97a2kTjIdse2uHpiQ6Q5lIY_HACKYwFWMdtT6l_nQBJeZfZJRk3GRlKEsvBI_wJMAltO9WwBQ6nK1qqKeRRc7gskTbqjkEvlIGEkYP3qEEvDSjBHBVLr5Mjr0CdGdPAbiBQ05YfoiCnFlfpWnuGea9Ey67svDdk257-9l-M8gXJC2foyuKri3hoyRycNIyavvn-rnQcf_s0qQRXBmMHddyjp8EUN84bowP8MaWIGybq-NPoh9RDQ7axLBmMlIMzEA2FNcdnJot43kgyFUNnjTNmMuF3_oXAKa5ooY4SHs28gyLS-ZcCCrOyn2QWE92ai03Ssy1ohZunrKHMAhzixgZM-xZwgaGO-1xsnFAHcEOlnxZMeHqLOG8sUIuF-mVLmf-sDtk6uJOsqtj8r40g1BpZArDqKbI7pG95nMsTBYtquaHvXAbQkaL22RP-x9ZEyCW0VirjuoUk4H615Wh6jLyoyA71q0aD829aMBZwaf3xpCRbKxwy_A2wTrQ0vygdxZDipws-KYL1FBLsSFSzVA4=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c3d000092cf2d05_0%7C0a220b774c40000011657e80_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EEF-z33U0bXO_BiIG8zNGmNEI0x7xnBb1yaNvXJ5ptySU4ks1gAzDLP2B2koOP27O27TsFzvmGWFpcCSpi75z-SGpUw1-iKf1XuJre1LBnuTjr_eyJuBzgQTid6aqtQtaL84I_Pqbi2BJoNcd_fLjDjzFyKCss_v29GkFRCjhAIGuZf3DMQxmFfUzGyNvstkGNpmdDJIKXOCE9tADbfgqA97a2kTjIdse2uHpiQ6Q5lIY_HACKYwFWMdtT6l_nQBJeZfZJRk3GRlKEsvBI_wJMAltO9WwBQ6nK1qqKeRRc7gskTbqjkEvlIGEkYP3qEEvDSjBHBVLr5Mjr0CdGdPAbiBQ05YfoiCnFlfpWnuGea9Ey67svDdk257-9l-M8gXJC2foyuKri3hoyRycNIyavvn-rnQcf_s0qQRXBmMHddyjp8EUN84bowP8MaWIGybq-NPoh9RDQ7axLBmMlIMzEA2FNcdnJot43kgyFUNnjTNmMuF3_oXAKa5ooY4SHs28gyLS-ZcCCrOyn2QWE92ai03Ssy1ohZunrKHMAhzixgZM-xZwgaGO-1xsnFAHcEOlnxZMeHqLOG8sUIuF-mVLmf-sDtk6uJOsqtj8r40g1BpZArDqKbI7pG95nMsTBYtquaHvXAbQkaL22RP-x9ZEyCW0VirjuoUk4H615Wh6jLyoyA71q0aD829aMBZwaf3xpCRbKxwy_A2wTrQ0vygdxZDipws-KYL1FBLsSFSzVA4=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-09T21:45:00.000Z", "utc_arrival": "2023-06-09T19:45:00.000Z", "local_departure": "2023-06-09T18:25:00.000Z", "utc_departure": "2023-06-09T16:25:00.000Z"}, {"id": "0b770a224c360000605964d6_0|0a220b774c3a0000b5d31f3b_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 603.284189, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 172393.6473, "conversion": {"EUR": 451.284569, "HUF": 172393.6473}, "fare": {"adults": 86196.82, "children": 86196.82, "infants": 86196.82}, "bags_price": {"1": 73.374, "2": 146.762}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 2}, "airlines": ["FR"], "route": [{"id": "0b770a224c360000605964d6_0", "combination_id": "0b770a224c360000605964d6", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-02T21:45:00.000Z", "utc_arrival": "2023-06-02T19:45:00.000Z", "local_departure": "2023-06-02T18:25:00.000Z", "utc_departure": "2023-06-02T16:25:00.000Z"}, {"id": "0a220b774c3a0000b5d31f3b_0", "combination_id": "0a220b774c3a0000b5d31f3b", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-06T14:05:00.000Z", "utc_arrival": "2023-06-06T12:05:00.000Z", "local_departure": "2023-06-06T10:55:00.000Z", "utc_departure": "2023-06-06T08:55:00.000Z"}], "booking_token": "EXbUekvBiDsRygEbyMlDRnalqH1DNLAaMLcHmm8WrBWsF31myIPiW8ztCr7gs8h739dD7ldZRha9zGfFr8A69-s1zr9Si3wptP8Ougdq6BCUkG3RgkU25LaBI7iIe6XA7aY4nCOIb-2vN_zX7nvzxkcNXoLsP-7VBFwJqYElO9NDFl_-_TgpgIyajvza-A6yX0lYJxOxiulV89BB_CsLnrDmUjcpiMq9BEijDCSlB433vWJ_Yb67UP8o2OGFlaVI1K94W7WuvNWbxLp0JbuINfm6Ob60gKa_qjrvayecV9QWl7y2a7LnE9sY6p3x2xT-UhNmZMi2knPS-PhZ5giPpc7CvAvb-8PDqzh80YHhHIotwOto83_czQuwg6IMTS6Zv-dSfXtM4oG5aCTHOgYqWT7hA74KoCghD4RiYhICWRrtfkGAR56wyjA7GGnbTREUrFn8pkrEQnej-ynj7frLo-xfOB6bYLX-MPW7ACnsGXS1YikVeeKnmH7GzVcdqbm2At_ckU8fJm1qkrlv8kaPL4-feYN1qCGbqjzrLL4b1x8QaAbtsgXL4fxYu6AQ3grEo8bjDe203AeowPakY0aGztBNpqXlrDRjxgh_xrIUCWWX3KJlkCBgBEyihOVmhzHT-g-04rt52a8H_T_ltd97O_jdHUveik-7XHLzy3wQmBXJdRzJRDoIMqcc5hg1dFCTJQ8d0jmQ3GV-mVDH3U9Ly_k4fztl1DhmqjTSKG43tKG4zVBmSzKyyFT2TnUtY8BpT", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c360000605964d6_0%7C0a220b774c3a0000b5d31f3b_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EXbUekvBiDsRygEbyMlDRnalqH1DNLAaMLcHmm8WrBWsF31myIPiW8ztCr7gs8h739dD7ldZRha9zGfFr8A69-s1zr9Si3wptP8Ougdq6BCUkG3RgkU25LaBI7iIe6XA7aY4nCOIb-2vN_zX7nvzxkcNXoLsP-7VBFwJqYElO9NDFl_-_TgpgIyajvza-A6yX0lYJxOxiulV89BB_CsLnrDmUjcpiMq9BEijDCSlB433vWJ_Yb67UP8o2OGFlaVI1K94W7WuvNWbxLp0JbuINfm6Ob60gKa_qjrvayecV9QWl7y2a7LnE9sY6p3x2xT-UhNmZMi2knPS-PhZ5giPpc7CvAvb-8PDqzh80YHhHIotwOto83_czQuwg6IMTS6Zv-dSfXtM4oG5aCTHOgYqWT7hA74KoCghD4RiYhICWRrtfkGAR56wyjA7GGnbTREUrFn8pkrEQnej-ynj7frLo-xfOB6bYLX-MPW7ACnsGXS1YikVeeKnmH7GzVcdqbm2At_ckU8fJm1qkrlv8kaPL4-feYN1qCGbqjzrLL4b1x8QaAbtsgXL4fxYu6AQ3grEo8bjDe203AeowPakY0aGztBNpqXlrDRjxgh_xrIUCWWX3KJlkCBgBEyihOVmhzHT-g-04rt52a8H_T_ltd97O_jdHUveik-7XHLzy3wQmBXJdRzJRDoIMqcc5hg1dFCTJQ8d0jmQ3GV-mVDH3U9Ly_k4fztl1DhmqjTSKG43tKG4zVBmSzKyyFT2TnUtY8BpT", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-02T21:45:00.000Z", "utc_arrival": "2023-06-02T19:45:00.000Z", "local_departure": "2023-06-02T18:25:00.000Z", "utc_departure": "2023-06-02T16:25:00.000Z"}, {"id": "0b770a224c3a0000c54ce2f2_0|0a220b774c3e0000a8664f90_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 609.149072, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 174634.0708, "conversion": {"EUR": 457.149452, "HUF": 174634.0708}, "fare": {"adults": 87317.04, "children": 87317.04, "infants": 87317.04}, "bags_price": {"1": 70.364, "2": 140.742}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 6}, "airlines": ["FR"], "route": [{"id": "0b770a224c3a0000c54ce2f2_0", "combination_id": "0b770a224c3a0000c54ce2f2", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-06T10:15:00.000Z", "utc_arrival": "2023-06-06T08:15:00.000Z", "local_departure": "2023-06-06T06:55:00.000Z", "utc_departure": "2023-06-06T04:55:00.000Z"}, {"id": "0a220b774c3e0000a8664f90_0", "combination_id": "0a220b774c3e0000a8664f90", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-10T09:40:00.000Z", "utc_arrival": "2023-06-10T07:40:00.000Z", "local_departure": "2023-06-10T06:30:00.000Z", "utc_departure": "2023-06-10T04:30:00.000Z"}], "booking_token": "EF0xa3m-HjzkKVyyS-58VBj5rlTpXm4dNAE1iyqgQFkhmgmC9QkU-1vco6klED_YdJwCHYATk2EOyQGthCzmUknbtKxm9FwEpH_P6NCGszTfc_B9HladigbVjsVwUMWLcqXEn-Pu-OIgzOYl4ZUxrW5QAkxsBb4-xv_CjKYlMg8QB7-dn_JpgNyP8KangM_orBawA4Is3w5Lkm6Z6m6SkU7nJw2flT6g93THKRFljjR24xmLYTp15spkBJ6CB_kZZKNwVfqpKjiXtxiaVjlH3MwLRkgk4rVzjdh20IwBDbhHPJmnly72jry81Nxejapu0MYiZNW8PVfif_raFcheVkVWLAoYh8Lb1l_hf9gyDwZthzPR0cmM1GcHFq1Jog2oPkW357rOx5QQDPTKJy08eoGEVdTTHuytFiwnLv6iQPzgxuauWBHVOSAmeeaqyRqOWAuEsHaDFkwOLtmjPrNufX4srDLk0vXiIJx4bCipxaMjckSyhJcimOZJW4AXvfR4o4NDcEdNkijmUUwHXf7z5yR3CFr8XSW6OYpVeqHyvNwUPkMTtlz7JXlYnr0ysYJb-yBv0178uCcSesUfWKjhkucH2xrCH3nc_Zmgk0mnRjWAX8oXxLRQZQmj855kvtkcdMUdDcqvX9J1FNXh4I1A8QlkCTPGhK1vajiVeczgLNIJPWkhB125UDodCIRlxKw_sXinTmH2XMtABsbMQmirAyMW_id1CI24_aPfs0H7niHI=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c3a0000c54ce2f2_0%7C0a220b774c3e0000a8664f90_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EF0xa3m-HjzkKVyyS-58VBj5rlTpXm4dNAE1iyqgQFkhmgmC9QkU-1vco6klED_YdJwCHYATk2EOyQGthCzmUknbtKxm9FwEpH_P6NCGszTfc_B9HladigbVjsVwUMWLcqXEn-Pu-OIgzOYl4ZUxrW5QAkxsBb4-xv_CjKYlMg8QB7-dn_JpgNyP8KangM_orBawA4Is3w5Lkm6Z6m6SkU7nJw2flT6g93THKRFljjR24xmLYTp15spkBJ6CB_kZZKNwVfqpKjiXtxiaVjlH3MwLRkgk4rVzjdh20IwBDbhHPJmnly72jry81Nxejapu0MYiZNW8PVfif_raFcheVkVWLAoYh8Lb1l_hf9gyDwZthzPR0cmM1GcHFq1Jog2oPkW357rOx5QQDPTKJy08eoGEVdTTHuytFiwnLv6iQPzgxuauWBHVOSAmeeaqyRqOWAuEsHaDFkwOLtmjPrNufX4srDLk0vXiIJx4bCipxaMjckSyhJcimOZJW4AXvfR4o4NDcEdNkijmUUwHXf7z5yR3CFr8XSW6OYpVeqHyvNwUPkMTtlz7JXlYnr0ysYJb-yBv0178uCcSesUfWKjhkucH2xrCH3nc_Zmgk0mnRjWAX8oXxLRQZQmj855kvtkcdMUdDcqvX9J1FNXh4I1A8QlkCTPGhK1vajiVeczgLNIJPWkhB125UDodCIRlxKw_sXinTmH2XMtABsbMQmirAyMW_id1CI24_aPfs0H7niHI=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-06T10:15:00.000Z", "utc_arrival": "2023-06-06T08:15:00.000Z", "local_departure": "2023-06-06T06:55:00.000Z", "utc_departure": "2023-06-06T04:55:00.000Z"}, {"id": "0b770a224c4100007151a3a5_0|0a220b774c44000078e26f99_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 612.293653, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 175835.3213, "conversion": {"EUR": 460.294033, "HUF": 175835.3213}, "fare": {"adults": 87917.66, "children": 87917.66, "infants": 87917.66}, "bags_price": {"1": 74.284, "2": 148.386}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 6}, "airlines": ["FR"], "route": [{"id": "0b770a224c4100007151a3a5_0", "combination_id": "0b770a224c4100007151a3a5", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-13T10:15:00.000Z", "utc_arrival": "2023-06-13T08:15:00.000Z", "local_departure": "2023-06-13T06:55:00.000Z", "utc_departure": "2023-06-13T04:55:00.000Z"}, {"id": "0a220b774c44000078e26f99_0", "combination_id": "0a220b774c44000078e26f99", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-16T18:00:00.000Z", "utc_arrival": "2023-06-16T16:00:00.000Z", "local_departure": "2023-06-16T14:50:00.000Z", "utc_departure": "2023-06-16T12:50:00.000Z"}], "booking_token": "EEmkCSzlwVJLFRi9KFi3FaUoaxDiBb_MwGLIsRxVzIwrmwUGi99jLD-t33n7bdunfl16964bwv9UkuNaMT-qvngIIXIH0Y0-j6QVk7-d9DJno-ivLVxNyhC_5B9ev-hNDTmBvZhdwbnZubs-sgLy9j8YhuD8TfksQjnWzWQ9ZAqlsHKYLQqjsJ1ZIyu1C5cy37DYkCbDMHuxwRy5Uaj7Aw0ATqt-4qYWrOG-ajnfzw0atLUvkwrO6oL-59p5rG-RwZpBIRhfdHzow4LbisHIYUUTOMYcG2tXtxeNFMxh36OXuas9sm31ljbhAxIIGYzawZ7SSGDbdw6JDj0YhZ7pTO1H0Q84Hhy5sVv-BmFjcWfsCX86sNRf-_uhSbWWO_g9NSU8ILT_ALZTm80wuGi-pqwyusbTvLkzmCdKD4AbffPBif5gydeKEp4dipZixRCUyJv6MbFVUwsbje15FWrNiBKCjGCS4xTe-CH6ouzEomS2nWWUP-tbBMfThoWG4IM7nIWElM4pT1uWxjVgGvBiHr8qMTseaXcYysTJr-ox6hu45nVOI4nVqs2LHKSU0HW3qwZQeom6Jq2rLMRxL3fPTbFDAUORPOi7PIYzSER_IKspjqG0nf0dhMIfrZZ7bON47t--gTwb8NxrSosXGGPBhWzhk8gQHvxbfGC0g5PEsXuwe3nzaSHCwWi4Gje0kIbTEnz0VzaKDqkKVreMSKhDUeg==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c4100007151a3a5_0%7C0a220b774c44000078e26f99_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EEmkCSzlwVJLFRi9KFi3FaUoaxDiBb_MwGLIsRxVzIwrmwUGi99jLD-t33n7bdunfl16964bwv9UkuNaMT-qvngIIXIH0Y0-j6QVk7-d9DJno-ivLVxNyhC_5B9ev-hNDTmBvZhdwbnZubs-sgLy9j8YhuD8TfksQjnWzWQ9ZAqlsHKYLQqjsJ1ZIyu1C5cy37DYkCbDMHuxwRy5Uaj7Aw0ATqt-4qYWrOG-ajnfzw0atLUvkwrO6oL-59p5rG-RwZpBIRhfdHzow4LbisHIYUUTOMYcG2tXtxeNFMxh36OXuas9sm31ljbhAxIIGYzawZ7SSGDbdw6JDj0YhZ7pTO1H0Q84Hhy5sVv-BmFjcWfsCX86sNRf-_uhSbWWO_g9NSU8ILT_ALZTm80wuGi-pqwyusbTvLkzmCdKD4AbffPBif5gydeKEp4dipZixRCUyJv6MbFVUwsbje15FWrNiBKCjGCS4xTe-CH6ouzEomS2nWWUP-tbBMfThoWG4IM7nIWElM4pT1uWxjVgGvBiHr8qMTseaXcYysTJr-ox6hu45nVOI4nVqs2LHKSU0HW3qwZQeom6Jq2rLMRxL3fPTbFDAUORPOi7PIYzSER_IKspjqG0nf0dhMIfrZZ7bON47t--gTwb8NxrSosXGGPBhWzhk8gQHvxbfGC0g5PEsXuwe3nzaSHCwWi4Gje0kIbTEnz0VzaKDqkKVreMSKhDUeg==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-13T10:15:00.000Z", "utc_arrival": "2023-06-13T08:15:00.000Z", "local_departure": "2023-06-13T06:55:00.000Z", "utc_departure": "2023-06-13T04:55:00.000Z"}, {"id": "0b770a224c430000a78af0de_0|0a220b774c4700009310bb78_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 616.106053, "distance": 1975.87, "duration": {"departure": 12600, "return": 11400, "total": 24000}, "price": 176273.0014, "conversion": {"EUR": 461.439773, "HUF": 176273.0014}, "fare": {"adults": 88136.5, "children": 88136.5, "infants": 88136.5}, "bags_price": {"1": 76.454, "2": 152.908}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 2}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224c430000a78af0de_0", "combination_id": "0b770a224c430000a78af0de", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IJREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-15T21:15:00.000Z", "utc_arrival": "2023-06-15T19:15:00.000Z", "local_departure": "2023-06-15T17:45:00.000Z", "utc_departure": "2023-06-15T15:45:00.000Z"}, {"id": "0a220b774c4700009310bb78_0", "combination_id": "0a220b774c4700009310bb78", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-19T10:15:00.000Z", "utc_arrival": "2023-06-19T08:15:00.000Z", "local_departure": "2023-06-19T07:05:00.000Z", "utc_departure": "2023-06-19T05:05:00.000Z"}], "booking_token": "EKL-Ch-1-b4gGj-gdhNJ06f0t11RGCygCXS-c0HmevcCm3UTboofUvUYFUk0eGLN3GHBHpW_EfQqF1sQ8Ud7cdnSFuz9Rr3F0WfwLLgLTAH2HCQBhzq9aCqp_W3qQOirTBMScxcSypeClPuTnTvpo9LerMwZqkDFEKD1aRJVS-C0PAHCBmj3D0vK2JEpUtJqtZGeBDKyPEqUTJMykNCKjyv-WANj3b6Gt90Eww1IHoBcVI5PvdNyq-s3RwyO7mZj-4b4SOkLvzdrbNRX_VPAQTzailG2-i2VZzt36DphTMkin3gNtJvb83cLvELrdZVqGRMAlfBFZlTwxK7mlBn3PXbkTAvV8EUx1HV_MmI1m0O-sCxCPzZdf3IR_seCZMQo7Xm6sPlGGwizrB_C-r13KB-kwRFUT7S1N6sl8sHecSqvDuNFMiblsi96FKIPhPi3HKWMQo5jqmch_It2b4O44Be1kLOp4jDSW8voc6moln50YuejkpVBipQyCn0M33dVQ9UAavxhNlxWo7vTN6K0ztckAWt8UC0Rm-mj7IhQLK4htdcMFs9ySLe_QxCLtr-J1zNVnpHtDXIovagnl1MGKMGfUvBzi_ucNtIgLDJ85P0QZBQRH-9ZXma2YRr-xmpsCMyQfoKqetC0ov0d51nXHNBPqOGr4907Qtq_pi4gC0NP8PRgZZ0RlfoE5zLTbuKZpkSRiK8ojRdiHHYedUG8SWkfsZvMjkvJYzlKrvzQyZWwsVfHWHg7MHh21u7BMCyU0DEUupjGnnBTOaBCNULJnRK2X0HHHNkgZ51mby9DCTKo=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c430000a78af0de_0%7C0a220b774c4700009310bb78_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EKL-Ch-1-b4gGj-gdhNJ06f0t11RGCygCXS-c0HmevcCm3UTboofUvUYFUk0eGLN3GHBHpW_EfQqF1sQ8Ud7cdnSFuz9Rr3F0WfwLLgLTAH2HCQBhzq9aCqp_W3qQOirTBMScxcSypeClPuTnTvpo9LerMwZqkDFEKD1aRJVS-C0PAHCBmj3D0vK2JEpUtJqtZGeBDKyPEqUTJMykNCKjyv-WANj3b6Gt90Eww1IHoBcVI5PvdNyq-s3RwyO7mZj-4b4SOkLvzdrbNRX_VPAQTzailG2-i2VZzt36DphTMkin3gNtJvb83cLvELrdZVqGRMAlfBFZlTwxK7mlBn3PXbkTAvV8EUx1HV_MmI1m0O-sCxCPzZdf3IR_seCZMQo7Xm6sPlGGwizrB_C-r13KB-kwRFUT7S1N6sl8sHecSqvDuNFMiblsi96FKIPhPi3HKWMQo5jqmch_It2b4O44Be1kLOp4jDSW8voc6moln50YuejkpVBipQyCn0M33dVQ9UAavxhNlxWo7vTN6K0ztckAWt8UC0Rm-mj7IhQLK4htdcMFs9ySLe_QxCLtr-J1zNVnpHtDXIovagnl1MGKMGfUvBzi_ucNtIgLDJ85P0QZBQRH-9ZXma2YRr-xmpsCMyQfoKqetC0ov0d51nXHNBPqOGr4907Qtq_pi4gC0NP8PRgZZ0RlfoE5zLTbuKZpkSRiK8ojRdiHHYedUG8SWkfsZvMjkvJYzlKrvzQyZWwsVfHWHg7MHh21u7BMCyU0DEUupjGnnBTOaBCNULJnRK2X0HHHNkgZ51mby9DCTKo=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-15T21:15:00.000Z", "utc_arrival": "2023-06-15T19:15:00.000Z", "local_departure": "2023-06-15T17:45:00.000Z", "utc_departure": "2023-06-15T15:45:00.000Z"}, {"id": "0b770a224c1900003bb4006b_0|0a220b774c1c00004005581a_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 617.507002, "distance": 1975.87, "duration": {"departure": 12600, "return": 11700, "total": 24300}, "price": 176298.8323, "conversion": {"EUR": 461.507392, "HUF": 176298.8323}, "fare": {"adults": 88149.42, "children": 88149.42, "infants": 88149.42}, "bags_price": {"1": 105.014, "2": 210.042}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 439, "hold_height": 149, "hold_length": 171, "hold_weight": 20, "hold_width": 119, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 3}, "airlines": ["W6"], "route": [{"id": "0b770a224c1900003bb4006b_0", "combination_id": "0b770a224c1900003bb4006b", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "KLREG", "fare_category": "M", "fare_classes": "K", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-04T21:15:00.000Z", "utc_arrival": "2023-05-04T19:15:00.000Z", "local_departure": "2023-05-04T17:45:00.000Z", "utc_departure": "2023-05-04T15:45:00.000Z"}, {"id": "0a220b774c1c00004005581a_0", "combination_id": "0a220b774c1c00004005581a", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "KREG", "fare_category": "M", "fare_classes": "K", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-07T21:05:00.000Z", "utc_arrival": "2023-05-07T19:05:00.000Z", "local_departure": "2023-05-07T17:50:00.000Z", "utc_departure": "2023-05-07T15:50:00.000Z"}], "booking_token": "ErgbccXUBt5uNWb0mf0hzpIK4ABsHOvROVlnQm8u9EEWSmexhHgUCBHBYlu76VW2Zl7JsKEhYY2aTXk1AbwfXwkdGRRID9HaFBbu36Qb2rswWRz1lpBBPRh6iE4beAXusij07xqrOEWIsTXXWu6BnAPmJD6OJGmL2fv-fmO6OIq94rRX5QTtXgf9TKnwyytjsUGDUKZKxmmOdHlPtb-_2L4MCgCiW0BGh3MuFb-D4ad9oov6XDH4spdicx_DQfhkqeZUfBC3mMrXEPWZoKU1hVQP4JjbNhIdwaSNzVCO-sdCVj5a02Lqxj0xu1UseljgRGeNeXoXrowo4ax6389RCfwlTHTcetiLONHD5NzP7SZmuPlYgegYdz1MJ9NPgTVKc3bd7FidUX8fxbCO2EXyMSPFko5SrNCJv8B1SkcIpeXW0QU6ZEGvbc2NK-no-C602EPgQdEZx4EMLt_2B3H_DJpcHmaLiyoszDmjcWQeqOP3krmL1k6tHLG8GyG040hmBqm0FiNAkev5VVG9wvfFJ5IsAdhvo1R0peg6VBgVTRQRN0OGE2XHYiz8sfKsKs0kTjWRtyxQNaTdaovVct4VvBNT0LglPVuVYanr6hWrulILQiIEgHrbU4zdl-HUX0P0Njh-VFCswOsmApCzQMuNfhMgygmW5KxgfPqj26VMTGifhUG0g5t8ag9ViQVk-jqnTOyhdAIFpMW2AYK1GHRJPRG5hvZ0euUKiRibMoU9a1hQ5TN3Sq6ZX5q6OX57iEfm1yyCqAZoBiukfvJ0SUtSo4CVlGQCAFdZYEbWmK6-Ybe0=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c1900003bb4006b_0%7C0a220b774c1c00004005581a_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=ErgbccXUBt5uNWb0mf0hzpIK4ABsHOvROVlnQm8u9EEWSmexhHgUCBHBYlu76VW2Zl7JsKEhYY2aTXk1AbwfXwkdGRRID9HaFBbu36Qb2rswWRz1lpBBPRh6iE4beAXusij07xqrOEWIsTXXWu6BnAPmJD6OJGmL2fv-fmO6OIq94rRX5QTtXgf9TKnwyytjsUGDUKZKxmmOdHlPtb-_2L4MCgCiW0BGh3MuFb-D4ad9oov6XDH4spdicx_DQfhkqeZUfBC3mMrXEPWZoKU1hVQP4JjbNhIdwaSNzVCO-sdCVj5a02Lqxj0xu1UseljgRGeNeXoXrowo4ax6389RCfwlTHTcetiLONHD5NzP7SZmuPlYgegYdz1MJ9NPgTVKc3bd7FidUX8fxbCO2EXyMSPFko5SrNCJv8B1SkcIpeXW0QU6ZEGvbc2NK-no-C602EPgQdEZx4EMLt_2B3H_DJpcHmaLiyoszDmjcWQeqOP3krmL1k6tHLG8GyG040hmBqm0FiNAkev5VVG9wvfFJ5IsAdhvo1R0peg6VBgVTRQRN0OGE2XHYiz8sfKsKs0kTjWRtyxQNaTdaovVct4VvBNT0LglPVuVYanr6hWrulILQiIEgHrbU4zdl-HUX0P0Njh-VFCswOsmApCzQMuNfhMgygmW5KxgfPqj26VMTGifhUG0g5t8ag9ViQVk-jqnTOyhdAIFpMW2AYK1GHRJPRG5hvZ0euUKiRibMoU9a1hQ5TN3Sq6ZX5q6OX57iEfm1yyCqAZoBiukfvJ0SUtSo4CVlGQCAFdZYEbWmK6-Ybe0=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-04T21:15:00.000Z", "utc_arrival": "2023-05-04T19:15:00.000Z", "local_departure": "2023-05-04T17:45:00.000Z", "utc_departure": "2023-05-04T15:45:00.000Z"}, {"id": "0b770a224c4800006d0d7298_0|0a220b774c4b0000292d2891_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 616.069675, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 177277.7863, "conversion": {"EUR": 464.070055, "HUF": 177277.7863}, "fare": {"adults": 88638.89, "children": 88638.89, "infants": 88638.89}, "bags_price": {"1": 77.826, "2": 155.638}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 3}, "airlines": ["FR"], "route": [{"id": "0b770a224c4800006d0d7298_0", "combination_id": "0b770a224c4800006d0d7298", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-20T10:15:00.000Z", "utc_arrival": "2023-06-20T08:15:00.000Z", "local_departure": "2023-06-20T06:55:00.000Z", "utc_departure": "2023-06-20T04:55:00.000Z"}, {"id": "0a220b774c4b0000292d2891_0", "combination_id": "0a220b774c4b0000292d2891", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-23T18:00:00.000Z", "utc_arrival": "2023-06-23T16:00:00.000Z", "local_departure": "2023-06-23T14:50:00.000Z", "utc_departure": "2023-06-23T12:50:00.000Z"}], "booking_token": "EnKxSjWDmM-tDcNgx9W7x3HjHi7zpXQZEXCyPoJUtJfa8lSfDnu5WX0tTNHFYIvXpsuziCshgVm0WAJUSDlv6NfRV7Qzg-KSgcXKjfgtEFNKMNCHELS9a1n155mpFZGA1y_cOUR9NMlhL8_59cUGpZtV3b1rmtLZ9gR28hqaaOLzkyMh63dfcrujmj88epJQZUsD3R27Q1hJCP7a46GkYQRkbck05j8h8GDpKjLlTnQlEPVqBGM1OTEFasd2V-uryOelXaOsv2MT4cIUuwu6KfE5ZwBt5yYjIQ-cnmvktzPB6tVREbq6Tf7bFW8bnk14mQrbFrJjK1mfRx3qfojCWXxer_vJtUTXNiWVPq2i0pKN4aFR7Qnuy02MDxgWirjq0Yut6kT-du45Et0xNfj7gKL4_xF5DGdG-muDFKlAfipOxBci_JSAoS2mJIKIsUvpoqM8D3d0dakNTRhBtPPbdnIZ7E5WzROGaTzOXWdHQhX1RVrw1OSOuoRrOBapkEz-yN3v52arSWfaU-e-OnR13GSpPUuJMHhHw8cT1bCEAAtkPMuYD1en_f6DIS-Ss-GZ4JDvhKjbulGYOuvQRn12XB571EcsgtjGfbYyrZlCC0UNzGKf4Kek1ctVLXWcy1jpPh6XubMBVwqP0Juxd8CeDoVI0C4Gk0Okn8R2E_WeQI_K7s2CT_PQPIUVfc89wIMPcaGu1TN2uuLcapAMVlEUd-zNnyOoW4dHFcBr9l2a4TUgcMNxUqkEcTC1Ve4FiteaR", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c4800006d0d7298_0%7C0a220b774c4b0000292d2891_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EnKxSjWDmM-tDcNgx9W7x3HjHi7zpXQZEXCyPoJUtJfa8lSfDnu5WX0tTNHFYIvXpsuziCshgVm0WAJUSDlv6NfRV7Qzg-KSgcXKjfgtEFNKMNCHELS9a1n155mpFZGA1y_cOUR9NMlhL8_59cUGpZtV3b1rmtLZ9gR28hqaaOLzkyMh63dfcrujmj88epJQZUsD3R27Q1hJCP7a46GkYQRkbck05j8h8GDpKjLlTnQlEPVqBGM1OTEFasd2V-uryOelXaOsv2MT4cIUuwu6KfE5ZwBt5yYjIQ-cnmvktzPB6tVREbq6Tf7bFW8bnk14mQrbFrJjK1mfRx3qfojCWXxer_vJtUTXNiWVPq2i0pKN4aFR7Qnuy02MDxgWirjq0Yut6kT-du45Et0xNfj7gKL4_xF5DGdG-muDFKlAfipOxBci_JSAoS2mJIKIsUvpoqM8D3d0dakNTRhBtPPbdnIZ7E5WzROGaTzOXWdHQhX1RVrw1OSOuoRrOBapkEz-yN3v52arSWfaU-e-OnR13GSpPUuJMHhHw8cT1bCEAAtkPMuYD1en_f6DIS-Ss-GZ4JDvhKjbulGYOuvQRn12XB571EcsgtjGfbYyrZlCC0UNzGKf4Kek1ctVLXWcy1jpPh6XubMBVwqP0Juxd8CeDoVI0C4Gk0Okn8R2E_WeQI_K7s2CT_PQPIUVfc89wIMPcaGu1TN2uuLcapAMVlEUd-zNnyOoW4dHFcBr9l2a4TUgcMNxUqkEcTC1Ve4FiteaR", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-20T10:15:00.000Z", "utc_arrival": "2023-06-20T08:15:00.000Z", "local_departure": "2023-06-20T06:55:00.000Z", "utc_departure": "2023-06-20T04:55:00.000Z"}, {"id": "0b770a224c440000087d9250_0|0a220b774c4800001d928f51_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 618.056308, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 178036.693, "conversion": {"EUR": 466.056688, "HUF": 178036.693}, "fare": {"adults": 89018.35, "children": 91837.39, "infants": 91837.39}, "bags_price": {"1": 82.88, "2": 173.348}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 3}, "airlines": ["FR"], "route": [{"id": "0b770a224c440000087d9250_0", "combination_id": "0b770a224c440000087d9250", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-16T21:45:00.000Z", "utc_arrival": "2023-06-16T19:45:00.000Z", "local_departure": "2023-06-16T18:25:00.000Z", "utc_departure": "2023-06-16T16:25:00.000Z"}, {"id": "0a220b774c4800001d928f51_0", "combination_id": "0a220b774c4800001d928f51", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-20T14:05:00.000Z", "utc_arrival": "2023-06-20T12:05:00.000Z", "local_departure": "2023-06-20T10:55:00.000Z", "utc_departure": "2023-06-20T08:55:00.000Z"}], "booking_token": "EGvfLcQGWQpUb8zBZB6AUleYFS2J-cfPEuwY8kk2FwuHqt3-w5Z9xQUBaVnWDbgrREfrcy1frhm8MiOor2LpuZsWHJ4UzjVS3ROo6xCbzLJQ7KagLxxIma7lxKa67RtZM4BJp4btvv3HeKEC9X1_rq9Zh6ZQQZukZ9qm80qyhQE9aHKo4xEp8qqjF1kNO1qhHohtX3Q9IXXl5DZwOcGrN8KEmwTvVmDOKunTxY92grHeHB2jh_DpjdBBJJu7JtgfEFFPqwt0-0fI-CohQxSiOniuSPS038ZTee1LYI6vr95tDDne8Z-KScAjwqgsPh1-zjd069q_mezbJVkhhJyF_yTkaMr-DlyGDUBIYK34UC1ZU82oiS7Hx9ayiOOVtwOlR27r0FhYU83uDUmmGfFtbsv7OFDsSefiDzIKU5KzPtNdBceC2P5s_SubgnKsJd4rjWSsZgHB3rGvSdr0qzG04B5qIJdMtziQZCFdK7Qp5PBF9Apue-d5A3Ro_J6Zsou-zWQHQpYelSF17MvztHYZCUHmFuQyW5375jFdbDHrscjPalKxegJ4Au4g-t_f4Vu8fg_6detkbEo8WjmXmQdWl9bqBvnfAFjH7vKvVsNNOb83RVVhnoTvKE956iyy-Pgj-xHfU2BsYqWvwp9V5b42y-T-xLI00dBsHsuj1MH5yqZIbyXwuJ_naZ3nA6epA3ldlxY5PDeZQjnjeG58EPetwc5BTBl5HzcRbRBGFtEgek_D-QeNuAIpWxFNL2eZhBHnLqPbd2Zk8y4PNwMvHINWxSw==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c440000087d9250_0%7C0a220b774c4800001d928f51_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EGvfLcQGWQpUb8zBZB6AUleYFS2J-cfPEuwY8kk2FwuHqt3-w5Z9xQUBaVnWDbgrREfrcy1frhm8MiOor2LpuZsWHJ4UzjVS3ROo6xCbzLJQ7KagLxxIma7lxKa67RtZM4BJp4btvv3HeKEC9X1_rq9Zh6ZQQZukZ9qm80qyhQE9aHKo4xEp8qqjF1kNO1qhHohtX3Q9IXXl5DZwOcGrN8KEmwTvVmDOKunTxY92grHeHB2jh_DpjdBBJJu7JtgfEFFPqwt0-0fI-CohQxSiOniuSPS038ZTee1LYI6vr95tDDne8Z-KScAjwqgsPh1-zjd069q_mezbJVkhhJyF_yTkaMr-DlyGDUBIYK34UC1ZU82oiS7Hx9ayiOOVtwOlR27r0FhYU83uDUmmGfFtbsv7OFDsSefiDzIKU5KzPtNdBceC2P5s_SubgnKsJd4rjWSsZgHB3rGvSdr0qzG04B5qIJdMtziQZCFdK7Qp5PBF9Apue-d5A3Ro_J6Zsou-zWQHQpYelSF17MvztHYZCUHmFuQyW5375jFdbDHrscjPalKxegJ4Au4g-t_f4Vu8fg_6detkbEo8WjmXmQdWl9bqBvnfAFjH7vKvVsNNOb83RVVhnoTvKE956iyy-Pgj-xHfU2BsYqWvwp9V5b42y-T-xLI00dBsHsuj1MH5yqZIbyXwuJ_naZ3nA6epA3ldlxY5PDeZQjnjeG58EPetwc5BTBl5HzcRbRBGFtEgek_D-QeNuAIpWxFNL2eZhBHnLqPbd2Zk8y4PNwMvHINWxSw==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-16T21:45:00.000Z", "utc_arrival": "2023-06-16T19:45:00.000Z", "local_departure": "2023-06-16T18:25:00.000Z", "utc_departure": "2023-06-16T16:25:00.000Z"}, {"id": "0b770a224c3e0000d8f9b259_0|0a220b774c41000001ce5e6c_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 620.62884, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 179019.417, "conversion": {"EUR": 468.62922, "HUF": 179019.417}, "fare": {"adults": 89509.71, "children": 89509.71, "infants": 89509.71}, "bags_price": {"1": 72.688, "2": 145.376}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 2}, "airlines": ["FR"], "route": [{"id": "0b770a224c3e0000d8f9b259_0", "combination_id": "0b770a224c3e0000d8f9b259", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-10T13:25:00.000Z", "utc_arrival": "2023-06-10T11:25:00.000Z", "local_departure": "2023-06-10T10:05:00.000Z", "utc_departure": "2023-06-10T08:05:00.000Z"}, {"id": "0a220b774c41000001ce5e6c_0", "combination_id": "0a220b774c41000001ce5e6c", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-13T14:05:00.000Z", "utc_arrival": "2023-06-13T12:05:00.000Z", "local_departure": "2023-06-13T10:55:00.000Z", "utc_departure": "2023-06-13T08:55:00.000Z"}], "booking_token": "EO6d626kjdGKZ2t1YjvEx0VzoXoxgeNrQKAPE0ZrCkDFt2nohzTY6g27uIZHxVaVSJBFUHk6ioQXtKKuQYW_PL7z8VG1pJZ0Ze3FUpruTvuLElPR6LcAZp4VeV1EwUJJAtwhLqkvnKtGDan4Ja2MZD2NzKzp6avBsU_7bZfJ-1hsRoJhdhNzdakqfBAjOm0EAuf8-qSy7tbea4caSXgxY1SWRqirbCaaDfq5HojWjiuiLHJtvB3VqcJDHxYiZX5w7csyYFKsPM7cZl5ryMCltVvXlkwSyiYwWuDEvsgObkZpaZmOWG8YMNZBHSk0zFWSMaNbHiSZsbxXXxk0ES0v9SHVLUIINYobwFfK5X9zJ-DPPAzEC4rpUKPU9ajiZpr4CEVQKCHJUDRqnC9zQorThoIMxEga9-JgKjh4peinFQSjFCcGAGtvRzAQ8MFxpin7_G3hcm1PAZjzrn1dvMXldg_JzyXIju0x57KElJBgH1RVlwg76HFw-HQPM_reDai9yCnQ_yueMKn6PLIh6gBdM_elOT1mvDM1CSzp4wIIQCo30FY0BNo43soSB4GGeGOV_RMt-2JPKuh2BAb2T6CcaEEuf4JNvjyHAb-dd25NlX2BBAMWHfejKyYJdW7ubpXLeDp6IMLbJC99SEzefT7_AeZ3q7XoJOpn6UO0pZ3uRSxGpyzfH8YWPcu0fpDqjBrD5PyktOYNq0uTRDuCYnTBxitSCbnxz26WxSh5HYHm8DzCgtCR_e12rzVQzxeYFQymZ", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c3e0000d8f9b259_0%7C0a220b774c41000001ce5e6c_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EO6d626kjdGKZ2t1YjvEx0VzoXoxgeNrQKAPE0ZrCkDFt2nohzTY6g27uIZHxVaVSJBFUHk6ioQXtKKuQYW_PL7z8VG1pJZ0Ze3FUpruTvuLElPR6LcAZp4VeV1EwUJJAtwhLqkvnKtGDan4Ja2MZD2NzKzp6avBsU_7bZfJ-1hsRoJhdhNzdakqfBAjOm0EAuf8-qSy7tbea4caSXgxY1SWRqirbCaaDfq5HojWjiuiLHJtvB3VqcJDHxYiZX5w7csyYFKsPM7cZl5ryMCltVvXlkwSyiYwWuDEvsgObkZpaZmOWG8YMNZBHSk0zFWSMaNbHiSZsbxXXxk0ES0v9SHVLUIINYobwFfK5X9zJ-DPPAzEC4rpUKPU9ajiZpr4CEVQKCHJUDRqnC9zQorThoIMxEga9-JgKjh4peinFQSjFCcGAGtvRzAQ8MFxpin7_G3hcm1PAZjzrn1dvMXldg_JzyXIju0x57KElJBgH1RVlwg76HFw-HQPM_reDai9yCnQ_yueMKn6PLIh6gBdM_elOT1mvDM1CSzp4wIIQCo30FY0BNo43soSB4GGeGOV_RMt-2JPKuh2BAb2T6CcaEEuf4JNvjyHAb-dd25NlX2BBAMWHfejKyYJdW7ubpXLeDp6IMLbJC99SEzefT7_AeZ3q7XoJOpn6UO0pZ3uRSxGpyzfH8YWPcu0fpDqjBrD5PyktOYNq0uTRDuCYnTBxitSCbnxz26WxSh5HYHm8DzCgtCR_e12rzVQzxeYFQymZ", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-10T13:25:00.000Z", "utc_arrival": "2023-06-10T11:25:00.000Z", "local_departure": "2023-06-10T10:05:00.000Z", "utc_departure": "2023-06-10T08:05:00.000Z"}, {"id": "0b770a224c4800006d0d7298_0|0a220b774c4b0000625e6e09_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 621.547128, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 179370.209, "conversion": {"EUR": 469.547508, "HUF": 179370.209}, "fare": {"adults": 89685.1, "children": 89685.1, "infants": 89685.1}, "bags_price": {"1": 76.454, "2": 162.708}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 158, "hold_height": 52, "hold_length": 78, "hold_weight": 20, "hold_width": 28, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 3, "personal_item_width": 15}, "availability": {"seats": 3}, "airlines": ["FR", "IB"], "route": [{"id": "0b770a224c4800006d0d7298_0", "combination_id": "0b770a224c4800006d0d7298", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-20T10:15:00.000Z", "utc_arrival": "2023-06-20T08:15:00.000Z", "local_departure": "2023-06-20T06:55:00.000Z", "utc_departure": "2023-06-20T04:55:00.000Z"}, {"id": "0a220b774c4b0000625e6e09_0", "combination_id": "0a220b774c4b0000625e6e09", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "IB", "flight_no": 3278, "operating_carrier": "IB", "operating_flight_no": "3278", "fare_basis": "QWNNAOB4", "fare_category": "M", "fare_classes": "Q", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-23T14:55:00.000Z", "utc_arrival": "2023-06-23T12:55:00.000Z", "local_departure": "2023-06-23T11:45:00.000Z", "utc_departure": "2023-06-23T09:45:00.000Z"}], "booking_token": "E0LIuMoVY06GBQLiWYDUdQduxws4OxYiMJtOxgyjptXBO16-sThkcc25mZed5vpRZm_JZ6w2_vNliKCTrDN4_7j4WXMe58OK9zULKj1dAgegWmRtVbXLm79nx_DL1rsF2HxATByqw_RHlGXtzDLI5RvOVeB-9GVPkrP2YJNQwXKma1D1yQ_hryLfbMG7E41tUH_hkK3Q0wRmTLmnwQ6Kvc66S7St_kjuTRI8__FmvVBMx_nIBb-1eZdMv8GTOppGXUioQc7dpyRkLfIU47aRV_GqqQKK16qMvZGdERjwMussXedWysi56Llv8I-1Pagikw5WtVaFeEEo6fHLMN1Ptiyrov1HBMsiCTMucYq_NYshHIxDjEeGmoTM7cJXjWVWxrOIzhOvvuSwA3R5IgYN9Hj94SNBiFC-5Dyb7zAaHydFJDTF3laLXC5lzvYJsNHAcDFB-nRihtibjDE4hq8ApQYlnVzRnm8Lv37dCuLXI2UhKfArfVtO_Pok2dkD3vakJ8_rx6Pckst-76KPoM-CBJKCHlKKgqv3TQhhTzyC0cAdrBzxmHcf0UhEtlehtE-pbrC5qj-gZtOriawWpVTYx3C_hRKXFTyFYzKYoSJS_Notq5WMKog0qvAuslQttWA5AJ-soR5d6fy1i3vpcEsU6EjY1Ap9-uTk2aorIJX2xo8sb1QQf1ucJuubf3QoSVUXTiR_Amlw_HAnUmsF8oY7tSgkvRXvR1Y_gz9bzRir1p8kuehszzoUP71Qlh6tZdPU3EN7DhYLmtDWZVuCMQIhgqy_7KqPpDEAwUIAXoqS5K0voI8BfBVmpAlEUoNpr4xIt", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c4800006d0d7298_0%7C0a220b774c4b0000625e6e09_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=E0LIuMoVY06GBQLiWYDUdQduxws4OxYiMJtOxgyjptXBO16-sThkcc25mZed5vpRZm_JZ6w2_vNliKCTrDN4_7j4WXMe58OK9zULKj1dAgegWmRtVbXLm79nx_DL1rsF2HxATByqw_RHlGXtzDLI5RvOVeB-9GVPkrP2YJNQwXKma1D1yQ_hryLfbMG7E41tUH_hkK3Q0wRmTLmnwQ6Kvc66S7St_kjuTRI8__FmvVBMx_nIBb-1eZdMv8GTOppGXUioQc7dpyRkLfIU47aRV_GqqQKK16qMvZGdERjwMussXedWysi56Llv8I-1Pagikw5WtVaFeEEo6fHLMN1Ptiyrov1HBMsiCTMucYq_NYshHIxDjEeGmoTM7cJXjWVWxrOIzhOvvuSwA3R5IgYN9Hj94SNBiFC-5Dyb7zAaHydFJDTF3laLXC5lzvYJsNHAcDFB-nRihtibjDE4hq8ApQYlnVzRnm8Lv37dCuLXI2UhKfArfVtO_Pok2dkD3vakJ8_rx6Pckst-76KPoM-CBJKCHlKKgqv3TQhhTzyC0cAdrBzxmHcf0UhEtlehtE-pbrC5qj-gZtOriawWpVTYx3C_hRKXFTyFYzKYoSJS_Notq5WMKog0qvAuslQttWA5AJ-soR5d6fy1i3vpcEsU6EjY1Ap9-uTk2aorIJX2xo8sb1QQf1ucJuubf3QoSVUXTiR_Amlw_HAnUmsF8oY7tSgkvRXvR1Y_gz9bzRir1p8kuehszzoUP71Qlh6tZdPU3EN7DhYLmtDWZVuCMQIhgqy_7KqPpDEAwUIAXoqS5K0voI8BfBVmpAlEUoNpr4xIt", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-20T10:15:00.000Z", "utc_arrival": "2023-06-20T08:15:00.000Z", "local_departure": "2023-06-20T06:55:00.000Z", "utc_departure": "2023-06-20T04:55:00.000Z"}, {"id": "0b770a224c330000e6ceb6e5_0|0a220b774c370000e3d9a22a_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 622.898131, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 179886.301, "conversion": {"EUR": 470.898511, "HUF": 179886.301}, "fare": {"adults": 89943.15, "children": 94312.59, "infants": 94312.59}, "bags_price": {"1": 69.678, "2": 139.356}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 6}, "airlines": ["FR"], "route": [{"id": "0b770a224c330000e6ceb6e5_0", "combination_id": "0b770a224c330000e6ceb6e5", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-30T10:15:00.000Z", "utc_arrival": "2023-05-30T08:15:00.000Z", "local_departure": "2023-05-30T06:55:00.000Z", "utc_departure": "2023-05-30T04:55:00.000Z"}, {"id": "0a220b774c370000e3d9a22a_0", "combination_id": "0a220b774c370000e3d9a22a", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-03T09:40:00.000Z", "utc_arrival": "2023-06-03T07:40:00.000Z", "local_departure": "2023-06-03T06:30:00.000Z", "utc_departure": "2023-06-03T04:30:00.000Z"}], "booking_token": "EuNJz6yHmHDvp4MDoFukfdFqrMJ9JC2Kpq1tiAC0EzSWcqpbVrTr-VHnEWZzsXFtaVuBUJlN57V2KG2aJuTNgdqyuowARkkob1v1kFnWSrcXx5368Djo6HCDgBxZ1rFspBnN8rRFswdC5yj6UUuXywYWnIuj05tEeFA_697VK5IhVDVkdttPZMiQfIZffDCuTTulwxDw-2kbXwM98BQFhKgtcEthV7mlFbrjOWdydGcxAlOC6053ti3idXG0fWDT1hzZ7FlarQBTLGdjEZWNhUZCeQDWd0dU13PGed8Wn9-dNM0fxrZObBML_eW68LLTcxWJs_mlyYv-20JE-7GhJ2pjK0wO_oa24oREdhC_-bqs8-Dps9x69LRhFQZatVQX28OP4Wdytg9jiCv4yDJGowsZwT_FIr5tMc0oYVtQQYRY5AZVCBILRd03FEdA_WO7Sti2C7xKWG2nBNsTdmTAO9KFFZlwxK6XtYiqtWpvNVMD2KC0Rn8IRY-HWAml7T34qQE5UUS_kw-Y1xeec4JuPEfNhYpIL1dzfLP7CJUXwhizdnsy61HlHa8-hCffc0bU85Ojh0UjQ5Hshp5GDwvfQvzNuMhLSfDo4p5rk248abn9_6-AlZtVpeCubRavaMPtTW9T0LzKUsmjVjyV-j-TQa1vzCiSNDACI0uOrniAK-pPDcP3QFizHjWUdTJBlQjk79RFys9rrkUCwlPmyyh-_PJEpui65PsRXgDwiITGMHsk=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c330000e6ceb6e5_0%7C0a220b774c370000e3d9a22a_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EuNJz6yHmHDvp4MDoFukfdFqrMJ9JC2Kpq1tiAC0EzSWcqpbVrTr-VHnEWZzsXFtaVuBUJlN57V2KG2aJuTNgdqyuowARkkob1v1kFnWSrcXx5368Djo6HCDgBxZ1rFspBnN8rRFswdC5yj6UUuXywYWnIuj05tEeFA_697VK5IhVDVkdttPZMiQfIZffDCuTTulwxDw-2kbXwM98BQFhKgtcEthV7mlFbrjOWdydGcxAlOC6053ti3idXG0fWDT1hzZ7FlarQBTLGdjEZWNhUZCeQDWd0dU13PGed8Wn9-dNM0fxrZObBML_eW68LLTcxWJs_mlyYv-20JE-7GhJ2pjK0wO_oa24oREdhC_-bqs8-Dps9x69LRhFQZatVQX28OP4Wdytg9jiCv4yDJGowsZwT_FIr5tMc0oYVtQQYRY5AZVCBILRd03FEdA_WO7Sti2C7xKWG2nBNsTdmTAO9KFFZlwxK6XtYiqtWpvNVMD2KC0Rn8IRY-HWAml7T34qQE5UUS_kw-Y1xeec4JuPEfNhYpIL1dzfLP7CJUXwhizdnsy61HlHa8-hCffc0bU85Ojh0UjQ5Hshp5GDwvfQvzNuMhLSfDo4p5rk248abn9_6-AlZtVpeCubRavaMPtTW9T0LzKUsmjVjyV-j-TQa1vzCiSNDACI0uOrniAK-pPDcP3QFizHjWUdTJBlQjk79RFys9rrkUCwlPmyyh-_PJEpui65PsRXgDwiITGMHsk=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-30T10:15:00.000Z", "utc_arrival": "2023-05-30T08:15:00.000Z", "local_departure": "2023-05-30T06:55:00.000Z", "utc_departure": "2023-05-30T04:55:00.000Z"}, {"id": "0b770a224c450000d9d313ec_0|0a220b774c48000056e1c9c9_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 634.007575, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 184130.181, "conversion": {"EUR": 482.007955, "HUF": 184130.181}, "fare": {"adults": 92065.09, "children": 92065.09, "infants": 92065.09}, "bags_price": {"1": 85.554, "2": 180.908}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 158, "hold_height": 52, "hold_length": 78, "hold_weight": 20, "hold_width": 28, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 3, "personal_item_width": 15}, "availability": {"seats": 3}, "airlines": ["FR", "IB"], "route": [{"id": "0b770a224c450000d9d313ec_0", "combination_id": "0b770a224c450000d9d313ec", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-17T13:25:00.000Z", "utc_arrival": "2023-06-17T11:25:00.000Z", "local_departure": "2023-06-17T10:05:00.000Z", "utc_departure": "2023-06-17T08:05:00.000Z"}, {"id": "0a220b774c48000056e1c9c9_0", "combination_id": "0a220b774c48000056e1c9c9", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "IB", "flight_no": 3278, "operating_carrier": "IB", "operating_flight_no": "3278", "fare_basis": "QDNNAOB4", "fare_category": "M", "fare_classes": "Q", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-20T14:55:00.000Z", "utc_arrival": "2023-06-20T12:55:00.000Z", "local_departure": "2023-06-20T11:45:00.000Z", "utc_departure": "2023-06-20T09:45:00.000Z"}], "booking_token": "EoEpF0aXaDXn1waArSw12PVsl7pIUptJ8GFMUteq3AuoC88zY7vq7K7TUZhToTlRJXzrOM1HoLLXB4oMsBThZN07joPy1n-9-iABBFI7r6wNhv2P2EvO-h7Gn4GCEsJU9aiFt1t6t8kzH84D_LxPdkbrN6FrQAQGEh4zFqwrUlrKoYSxC4jeIc5fJY8guOxLAwzkicVraGllrrZ0gnYI8Hfg3JGrwY3nQD0-gVeHayEqtkYGAsE9cRR8aT7DVa63b6pRTBO-5b0p4ZmRNlJDX9eNjG6-qhBDO3DBAqoVTTiY7vekUeFkjJZb24nakaTvV1_4Rafi72wdHGii0GhfY9DbMSX5xT59L7IRgwG8p3tyWFftZ545r7SBm4dLLsBhsBYugPsFelQNm8_5uMN-4GtMmpWXb_4lg1MjtPSLVepP3jJ_0E8cZDPsM-g7gZn4EwT8DISYHB8AFwDz321VfBmnf7TwwwhpVvQ1zUlvRZiGdmmBaMythakOtkrHdeXVDX_IozoH46W_4zsGSvxSackZOY1erD4JCoF_r4BCtMTsF0A_s2NzSSBWok5ugwwfuw4Tugf5KFpRBnR2te8qOhnhBYdwb3ikbjqGi_HjBbpFNFi9wMmEJlYgxpfiRYydpV8GDtQ8S38ERbfIIB8sPYcjBI__WvE_O6THsxl9Uboj6sVu8Idu3WkikpwcLqgO_q-D-Grm837vKemnMLAr2bw99WmVplWPvKwilw1zEQqe7Oict6c-0c5qyxE9gntfhFup9KSZ-Cj3vUcRQ5oKFGA==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c450000d9d313ec_0%7C0a220b774c48000056e1c9c9_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EoEpF0aXaDXn1waArSw12PVsl7pIUptJ8GFMUteq3AuoC88zY7vq7K7TUZhToTlRJXzrOM1HoLLXB4oMsBThZN07joPy1n-9-iABBFI7r6wNhv2P2EvO-h7Gn4GCEsJU9aiFt1t6t8kzH84D_LxPdkbrN6FrQAQGEh4zFqwrUlrKoYSxC4jeIc5fJY8guOxLAwzkicVraGllrrZ0gnYI8Hfg3JGrwY3nQD0-gVeHayEqtkYGAsE9cRR8aT7DVa63b6pRTBO-5b0p4ZmRNlJDX9eNjG6-qhBDO3DBAqoVTTiY7vekUeFkjJZb24nakaTvV1_4Rafi72wdHGii0GhfY9DbMSX5xT59L7IRgwG8p3tyWFftZ545r7SBm4dLLsBhsBYugPsFelQNm8_5uMN-4GtMmpWXb_4lg1MjtPSLVepP3jJ_0E8cZDPsM-g7gZn4EwT8DISYHB8AFwDz321VfBmnf7TwwwhpVvQ1zUlvRZiGdmmBaMythakOtkrHdeXVDX_IozoH46W_4zsGSvxSackZOY1erD4JCoF_r4BCtMTsF0A_s2NzSSBWok5ugwwfuw4Tugf5KFpRBnR2te8qOhnhBYdwb3ikbjqGi_HjBbpFNFi9wMmEJlYgxpfiRYydpV8GDtQ8S38ERbfIIB8sPYcjBI__WvE_O6THsxl9Uboj6sVu8Idu3WkikpwcLqgO_q-D-Grm837vKemnMLAr2bw99WmVplWPvKwilw1zEQqe7Oict6c-0c5qyxE9gntfhFup9KSZ-Cj3vUcRQ5oKFGA==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-17T13:25:00.000Z", "utc_arrival": "2023-06-17T11:25:00.000Z", "local_departure": "2023-06-17T10:05:00.000Z", "utc_departure": "2023-06-17T08:05:00.000Z"}, {"id": "0b770a224c3a0000c54ce2f2_0|0a220b774c3d0000e250d0cc_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 639.750195, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 186323.8993, "conversion": {"EUR": 487.750575, "HUF": 186323.8993}, "fare": {"adults": 93161.95, "children": 93161.95, "infants": 93161.95}, "bags_price": {"1": 70.364, "2": 141.246}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 6}, "airlines": ["FR"], "route": [{"id": "0b770a224c3a0000c54ce2f2_0", "combination_id": "0b770a224c3a0000c54ce2f2", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-06T10:15:00.000Z", "utc_arrival": "2023-06-06T08:15:00.000Z", "local_departure": "2023-06-06T06:55:00.000Z", "utc_departure": "2023-06-06T04:55:00.000Z"}, {"id": "0a220b774c3d0000e250d0cc_0", "combination_id": "0a220b774c3d0000e250d0cc", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-09T18:00:00.000Z", "utc_arrival": "2023-06-09T16:00:00.000Z", "local_departure": "2023-06-09T14:50:00.000Z", "utc_departure": "2023-06-09T12:50:00.000Z"}], "booking_token": "ETiFnQER4DQddTE1d3abHsfol5wl6Y9A4hvq__Wlxv6kuCiw-sRMvllm73lNpbCXNJyaqQjhYvO-JnoGHwJkWBhnEk4lcPbs4XyEIujrlG1SdR9KT5X2lFrAdsrLFMPYmAmvlzi3KDk0vePFwqGZXn0i5bDd5ey9SzRwtU2b52E6BdwTrwjIBAT_oBKN9EOEUarb4AS0UrEZpOX3nT9v0Kfjwr1pqeswLfzlREncFyMxKs2-Jlzw3BmdMzuea58sTRMwpXB6XTDxHV3BE3mb6qc1mRtPmeLupGVmt3eN7FXvV6TfVvCJcWJXoziwWlLB8BX26GJDJQZZalPJ0FaD3ZxpvdzNa2VjwmR6c71u_5AjgfAj0yVG3kc-8mFAlsw0cuUiavT6W6f9V89UD2fSHQTtPIhd4W8ctEeM559Puul5c6A74hT7E23AomaDPn8gd8dgQOC1hunwUo9hVxhvpFZ9aqjh_k5_-yuKiOAhVtgI_2jHAOSD4y5x9kpkAdtpHnIprp_BIk9dZcUvsc9sB0sShvbocy0az6lVqIKm6cNXf5QUhOkPhSQjxldwwJhDV2y_eE3rSVtWp44cpVk9gqm6-XE7sbNUt1ocxcEwEumtzCk-WE-fHJsW1t9bbnB1bNPg_wl0CbY3ULjxefCFT6ypOd1Mm8zBzUGWho2SfP4YVPGaCdFbg3QKxOyIN1K7D-2aACLynrmuI5xmJX4DfPQ==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c3a0000c54ce2f2_0%7C0a220b774c3d0000e250d0cc_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=ETiFnQER4DQddTE1d3abHsfol5wl6Y9A4hvq__Wlxv6kuCiw-sRMvllm73lNpbCXNJyaqQjhYvO-JnoGHwJkWBhnEk4lcPbs4XyEIujrlG1SdR9KT5X2lFrAdsrLFMPYmAmvlzi3KDk0vePFwqGZXn0i5bDd5ey9SzRwtU2b52E6BdwTrwjIBAT_oBKN9EOEUarb4AS0UrEZpOX3nT9v0Kfjwr1pqeswLfzlREncFyMxKs2-Jlzw3BmdMzuea58sTRMwpXB6XTDxHV3BE3mb6qc1mRtPmeLupGVmt3eN7FXvV6TfVvCJcWJXoziwWlLB8BX26GJDJQZZalPJ0FaD3ZxpvdzNa2VjwmR6c71u_5AjgfAj0yVG3kc-8mFAlsw0cuUiavT6W6f9V89UD2fSHQTtPIhd4W8ctEeM559Puul5c6A74hT7E23AomaDPn8gd8dgQOC1hunwUo9hVxhvpFZ9aqjh_k5_-yuKiOAhVtgI_2jHAOSD4y5x9kpkAdtpHnIprp_BIk9dZcUvsc9sB0sShvbocy0az6lVqIKm6cNXf5QUhOkPhSQjxldwwJhDV2y_eE3rSVtWp44cpVk9gqm6-XE7sbNUt1ocxcEwEumtzCk-WE-fHJsW1t9bbnB1bNPg_wl0CbY3ULjxefCFT6ypOd1Mm8zBzUGWho2SfP4YVPGaCdFbg3QKxOyIN1K7D-2aACLynrmuI5xmJX4DfPQ==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-06T10:15:00.000Z", "utc_arrival": "2023-06-06T08:15:00.000Z", "local_departure": "2023-06-06T06:55:00.000Z", "utc_departure": "2023-06-06T04:55:00.000Z"}, {"id": "0b770a224c4c0000c66587fd_0|0a220b774c4f0000a7608cfc_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 642.779759, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 187481.2125, "conversion": {"EUR": 490.780139, "HUF": 187481.2125}, "fare": {"adults": 93740.61, "children": 93740.61, "infants": 93740.61}, "bags_price": {"1": 86.016, "2": 172.032}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 2}, "airlines": ["FR"], "route": [{"id": "0b770a224c4c0000c66587fd_0", "combination_id": "0b770a224c4c0000c66587fd", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-24T13:25:00.000Z", "utc_arrival": "2023-06-24T11:25:00.000Z", "local_departure": "2023-06-24T10:05:00.000Z", "utc_departure": "2023-06-24T08:05:00.000Z"}, {"id": "0a220b774c4f0000a7608cfc_0", "combination_id": "0a220b774c4f0000a7608cfc", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-27T14:05:00.000Z", "utc_arrival": "2023-06-27T12:05:00.000Z", "local_departure": "2023-06-27T10:55:00.000Z", "utc_departure": "2023-06-27T08:55:00.000Z"}], "booking_token": "EfpmXQKVehFAbHLtFG6dxZC4C4_svsisJB5qZDbfSgBX6imD_ROfvoKGalOQMZoh2122TmDIVkTYMXcDZa7frY-P_lnVJsj3LH_CtLeFl15yt4SZwSIhCAigsP8v897aZELNLN2Uc1Nse73CIyGUC9Hm5NbUpJRiKSKo7iqaH7_sdqwojn7HjXAq4kcIdTKNl4TZKa0uHiTPmNgrjTKRTJLmgaFw41k3QIfTCB4U3L9hSCDDEmhrlZJme-5YRrNm8n-m87SZYAocNHK38cs9i2YGHhen0uk5Ib96lIdX_04EHD3hxM3C1Zr2ogNz8H39rYLjoR4ulJzbfow8e_bRUr6WUioIpNsk_TSDX9SSBZulAeHefAe3RkwlEqoDlIktQj_IdQSGrlzA4cjA3MvW15Shu4xMYj04SHemNa2a3-KO5__5osYkdH5A_Z63hZghgJeGmNFfHJRmhPuwEPAouGbMC7_b_6xUrA0U61JgDYMaoeV3MpOiT3R0t2HVtUYzx5g1nCbx0pHIkO7_IDXQ9oRk9unIZD4Aesc1Ihjw3furSXf9N6q5YOvL-e4aKctTlxm6sZBnSyGAmrtyhIh8GXVDQ7ndvkbPeIfBsbOzmi4xiUk4NJJW9leex89IDeSL0J4L3_0Uljdte55lrnxG5HnC30GKiMICwfHz_C4O2Re3-ImXBJHURbliDCnq3itj-vGIQGi_1rZnyIKRypWEo5A==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c4c0000c66587fd_0%7C0a220b774c4f0000a7608cfc_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EfpmXQKVehFAbHLtFG6dxZC4C4_svsisJB5qZDbfSgBX6imD_ROfvoKGalOQMZoh2122TmDIVkTYMXcDZa7frY-P_lnVJsj3LH_CtLeFl15yt4SZwSIhCAigsP8v897aZELNLN2Uc1Nse73CIyGUC9Hm5NbUpJRiKSKo7iqaH7_sdqwojn7HjXAq4kcIdTKNl4TZKa0uHiTPmNgrjTKRTJLmgaFw41k3QIfTCB4U3L9hSCDDEmhrlZJme-5YRrNm8n-m87SZYAocNHK38cs9i2YGHhen0uk5Ib96lIdX_04EHD3hxM3C1Zr2ogNz8H39rYLjoR4ulJzbfow8e_bRUr6WUioIpNsk_TSDX9SSBZulAeHefAe3RkwlEqoDlIktQj_IdQSGrlzA4cjA3MvW15Shu4xMYj04SHemNa2a3-KO5__5osYkdH5A_Z63hZghgJeGmNFfHJRmhPuwEPAouGbMC7_b_6xUrA0U61JgDYMaoeV3MpOiT3R0t2HVtUYzx5g1nCbx0pHIkO7_IDXQ9oRk9unIZD4Aesc1Ihjw3furSXf9N6q5YOvL-e4aKctTlxm6sZBnSyGAmrtyhIh8GXVDQ7ndvkbPeIfBsbOzmi4xiUk4NJJW9leex89IDeSL0J4L3_0Uljdte55lrnxG5HnC30GKiMICwfHz_C4O2Re3-ImXBJHURbliDCnq3itj-vGIQGi_1rZnyIKRypWEo5A==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-24T13:25:00.000Z", "utc_arrival": "2023-06-24T11:25:00.000Z", "local_departure": "2023-06-24T10:05:00.000Z", "utc_departure": "2023-06-24T08:05:00.000Z"}, {"id": "0b770a224c360000605964d6_0|0a220b774c390000563d5408_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 645.56272, "distance": 1975.87, "duration": {"departure": 12000, "return": 11700, "total": 23700}, "price": 188034.981, "conversion": {"EUR": 492.22977, "HUF": 188034.981}, "fare": {"adults": 94017.49, "children": 97322.84, "infants": 97322.84}, "bags_price": {"1": 95.396, "2": 190.792}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 2}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224c360000605964d6_0", "combination_id": "0b770a224c360000605964d6", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-02T21:45:00.000Z", "utc_arrival": "2023-06-02T19:45:00.000Z", "local_departure": "2023-06-02T18:25:00.000Z", "utc_departure": "2023-06-02T16:25:00.000Z"}, {"id": "0a220b774c390000563d5408_0", "combination_id": "0a220b774c390000563d5408", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-05T23:45:00.000Z", "utc_arrival": "2023-06-05T21:45:00.000Z", "local_departure": "2023-06-05T20:30:00.000Z", "utc_departure": "2023-06-05T18:30:00.000Z"}], "booking_token": "ERD0fxH-vzCkoVHCEru47aOORm3AunX3myzwB-NWJugXaOMMkp0EBBPpaYgn0PCp645-jjXTDn57VHGRlRkY2PzSfXqbl1bFo9g0hhHoLfPE6u6r6qOGQJqCtNYo5_wt71WML4TSdBETIeF9W47pjC9UZEBMj2iOZhJU844lTMuf8pZXHkIY65P-bHtry3VxqAfgmQfjSuYA-v7_Lix8Cnu-BamwfkZYl4Ko2Gr78vpO8bItUnkVpAZ83eojW2Sa37JSYL1_ATIeG3E2--RjWLKCF9Jbjezfcz_fPv4o3u9aMEIV9y7k5Ck9P1GL3xTX9uNLZy4lLo2ciJNf5DRCPVm2rzDN-nTh326uxgJQOU4girU9CoA8aheF8NGJTMtRcHtZK1ZcU_uTXCZOrvZOAgFLIjS27E2eRBzAyE9yJQGyN_U8iLixMCXF5EbUpLCbWEDJhKQPRMkJYXhRTgLoa9NVNFe7nCunIgzgQlh5JdZ9MeBLlcIZT1-DJrg3NdMrND_MhEmdvNZ_cBoQfzYsWx3h3EuPLTHOtLhizmR6uHv7BX5AhbQ8MQOK5j_BXM0a_M3Bq4h_RZqb09zL1Nm1HSfd6K4gApfy-7ANOM6y3xkLmSdslGokhimL08LLxQ7NlqVuMdTVPh3KQMyD_VWkQXKBNaA-XA3p0dF6EnN8cmhtZYTJ9rtERzwWWxqxwPIzSDN9bd6nU725v-IAgsKkTxJa09F3FadVLcTcLnDpb3JG6IOXtWiGJeRTiugN3hVQPXdisUYhWdG31_atkOaKaNg==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c360000605964d6_0%7C0a220b774c390000563d5408_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=ERD0fxH-vzCkoVHCEru47aOORm3AunX3myzwB-NWJugXaOMMkp0EBBPpaYgn0PCp645-jjXTDn57VHGRlRkY2PzSfXqbl1bFo9g0hhHoLfPE6u6r6qOGQJqCtNYo5_wt71WML4TSdBETIeF9W47pjC9UZEBMj2iOZhJU844lTMuf8pZXHkIY65P-bHtry3VxqAfgmQfjSuYA-v7_Lix8Cnu-BamwfkZYl4Ko2Gr78vpO8bItUnkVpAZ83eojW2Sa37JSYL1_ATIeG3E2--RjWLKCF9Jbjezfcz_fPv4o3u9aMEIV9y7k5Ck9P1GL3xTX9uNLZy4lLo2ciJNf5DRCPVm2rzDN-nTh326uxgJQOU4girU9CoA8aheF8NGJTMtRcHtZK1ZcU_uTXCZOrvZOAgFLIjS27E2eRBzAyE9yJQGyN_U8iLixMCXF5EbUpLCbWEDJhKQPRMkJYXhRTgLoa9NVNFe7nCunIgzgQlh5JdZ9MeBLlcIZT1-DJrg3NdMrND_MhEmdvNZ_cBoQfzYsWx3h3EuPLTHOtLhizmR6uHv7BX5AhbQ8MQOK5j_BXM0a_M3Bq4h_RZqb09zL1Nm1HSfd6K4gApfy-7ANOM6y3xkLmSdslGokhimL08LLxQ7NlqVuMdTVPh3KQMyD_VWkQXKBNaA-XA3p0dF6EnN8cmhtZYTJ9rtERzwWWxqxwPIzSDN9bd6nU725v-IAgsKkTxJa09F3FadVLcTcLnDpb3JG6IOXtWiGJeRTiugN3hVQPXdisUYhWdG31_atkOaKaNg==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-02T21:45:00.000Z", "utc_arrival": "2023-06-02T19:45:00.000Z", "local_departure": "2023-06-02T18:25:00.000Z", "utc_departure": "2023-06-02T16:25:00.000Z"}, {"id": "0b770a224c37000093465fe3_0|0a220b774c3a0000b5d31f3b_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 644.61578, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 188182.5845, "conversion": {"EUR": 492.61616, "HUF": 188182.5845}, "fare": {"adults": 94091.29, "children": 94091.29, "infants": 94091.29}, "bags_price": {"1": 75.88, "2": 151.774}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 6}, "airlines": ["FR"], "route": [{"id": "0b770a224c37000093465fe3_0", "combination_id": "0b770a224c37000093465fe3", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-03T13:25:00.000Z", "utc_arrival": "2023-06-03T11:25:00.000Z", "local_departure": "2023-06-03T10:05:00.000Z", "utc_departure": "2023-06-03T08:05:00.000Z"}, {"id": "0a220b774c3a0000b5d31f3b_0", "combination_id": "0a220b774c3a0000b5d31f3b", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-06T14:05:00.000Z", "utc_arrival": "2023-06-06T12:05:00.000Z", "local_departure": "2023-06-06T10:55:00.000Z", "utc_departure": "2023-06-06T08:55:00.000Z"}], "booking_token": "E8_jrfBZoRrpAszj9bXYU8zLL5F7rA5aqkmpOwSc_72vmwKLoUujCxLuzSHAEgDseQ_CqWZ2euCF5UZCAvmLXV9VVQgCshI6rsK4Sn42h-zvgFthGkb1u7JBxa_iNqD_Y5yYx26bO7Nrlw_hd6SE92kxNOO2K2bBapcyNUWRGk40MhqLOdV6eYyLNoAVpkC6Mwa2SD97EB2CYIS8TN52KYZK8d_w2jJ7mte1HU_4BCkQAxfOtX8_eQbBxiXMfqZox6flW48e1RTQhxl17IQ0S3YdQnnmINbrt_L8OAH3X03LtLDd40UmD65agdTML12O1fgqcecoibpuRgHVXjvJ9CJsp16RKcmL-_kCalUNEJWwK2oig7BjaGmpz67_08j9SW9Kwe0yNNLv4JH-uCNctKYSegtT-aAHnMI5MJYefZk9tkid6F-jcty2T_fk5obRQBFY_qFLnrkVMCEpHYyN5pDfuaAOyyLJluG6_jhKmDPP1RyhQpjhTLnYfYUR2Om2mBac--U3QFWW4E2TKbAOkWdhvK-pW5xH-9idtE542kGfAwSBUetdY46GrqMV70-g0iGVDUJQ25rTDl1h0FIgQtCtKSfTVmbRnENpQ85vTqDJSP5CVUfpgO2oLtTUHMgVcik4gTY3qWC8Z8pa-YXbdWeUg3MQbDVWDmL5gxR_QksM35YVbiFgDHPJ0rfp1Im8W1bbDpDZDUsX2V6YOv1a2Hw==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c37000093465fe3_0%7C0a220b774c3a0000b5d31f3b_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=E8_jrfBZoRrpAszj9bXYU8zLL5F7rA5aqkmpOwSc_72vmwKLoUujCxLuzSHAEgDseQ_CqWZ2euCF5UZCAvmLXV9VVQgCshI6rsK4Sn42h-zvgFthGkb1u7JBxa_iNqD_Y5yYx26bO7Nrlw_hd6SE92kxNOO2K2bBapcyNUWRGk40MhqLOdV6eYyLNoAVpkC6Mwa2SD97EB2CYIS8TN52KYZK8d_w2jJ7mte1HU_4BCkQAxfOtX8_eQbBxiXMfqZox6flW48e1RTQhxl17IQ0S3YdQnnmINbrt_L8OAH3X03LtLDd40UmD65agdTML12O1fgqcecoibpuRgHVXjvJ9CJsp16RKcmL-_kCalUNEJWwK2oig7BjaGmpz67_08j9SW9Kwe0yNNLv4JH-uCNctKYSegtT-aAHnMI5MJYefZk9tkid6F-jcty2T_fk5obRQBFY_qFLnrkVMCEpHYyN5pDfuaAOyyLJluG6_jhKmDPP1RyhQpjhTLnYfYUR2Om2mBac--U3QFWW4E2TKbAOkWdhvK-pW5xH-9idtE542kGfAwSBUetdY46GrqMV70-g0iGVDUJQ25rTDl1h0FIgQtCtKSfTVmbRnENpQ85vTqDJSP5CVUfpgO2oLtTUHMgVcik4gTY3qWC8Z8pa-YXbdWeUg3MQbDVWDmL5gxR_QksM35YVbiFgDHPJ0rfp1Im8W1bbDpDZDUsX2V6YOv1a2Hw==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-03T13:25:00.000Z", "utc_arrival": "2023-06-03T11:25:00.000Z", "local_departure": "2023-06-03T10:05:00.000Z", "utc_departure": "2023-06-03T08:05:00.000Z"}, {"id": "0b770a224c390000dc0e5ade_0|0a220b774c3d0000e250d0cc_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 645.467375, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 188507.8993, "conversion": {"EUR": 493.467755, "HUF": 188507.8993}, "fare": {"adults": 94253.95, "children": 94253.95, "infants": 94253.95}, "bags_price": {"1": 70.364, "2": 141.246}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 6}, "airlines": ["FR"], "route": [{"id": "0b770a224c390000dc0e5ade_0", "combination_id": "0b770a224c390000dc0e5ade", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-05T14:00:00.000Z", "utc_arrival": "2023-06-05T12:00:00.000Z", "local_departure": "2023-06-05T10:40:00.000Z", "utc_departure": "2023-06-05T08:40:00.000Z"}, {"id": "0a220b774c3d0000e250d0cc_0", "combination_id": "0a220b774c3d0000e250d0cc", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-09T18:00:00.000Z", "utc_arrival": "2023-06-09T16:00:00.000Z", "local_departure": "2023-06-09T14:50:00.000Z", "utc_departure": "2023-06-09T12:50:00.000Z"}], "booking_token": "Erhvs6pPh2PKnoGOVOuU955fk6IWPGxb9bd9DZAgIvv1jh3sSRl0OJJ01L0AhjZiOrX461b9GWZAtkaaS8luF7mkFD8_FFvACADpAYBMr81VG5Q29wgPPymxZgS77LSb8uIXIWzC3AfIs3qMiXAGPd4KKM2VT_KIlYnKGD5bQPXXKYmAobMt_X9CDl9XMlxEmbL0twZrtC5ALTzuC1tc2fiY8Rb256Q7s3A1wPce6ojbok_iH-SzUhNtpODj9CCiuzm2uoJ0N--VGrskOuyxz95ELthBoXN2grr68ipl0PKlnUDL0r9DT7r9Q0cIf2CfLozCyuoGIjWIZ-oYz0WKWuxtWIbTCdO7v2CFVtqgpdpB1pvmB1bUYASSvsIqWt4GKsFtMtnj1cdppbtLKJP3aU9_muLqzkNmyGuj2ch2lu0ZpiEHHJ7XGbLCBqFyfair8AdsNYPQKi6iJ0TQjhsaQuNRlinrQerTqPpX1EgSVdi8B9ONLlqOMzRPdlQPiaMXnitI-apmIFENG4chYNda_EzNsAlD5M6iqMM8XW9d1HB1oLGYtX0q1S-xfoUDqyMZkEJILhrRdzHaeOI1EMCR9_WHk-zeykslBOSjGyAilhxJITKY7t57kK3roOZVdpeFKIebs7CNt4_dv96TVxrmn0dTQG3p905Q68Xurn0y62AeDqOFjDF3E6nsNel_YdTF7AkqmvqQXfU8Pz40aI60dQQ==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c390000dc0e5ade_0%7C0a220b774c3d0000e250d0cc_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=Erhvs6pPh2PKnoGOVOuU955fk6IWPGxb9bd9DZAgIvv1jh3sSRl0OJJ01L0AhjZiOrX461b9GWZAtkaaS8luF7mkFD8_FFvACADpAYBMr81VG5Q29wgPPymxZgS77LSb8uIXIWzC3AfIs3qMiXAGPd4KKM2VT_KIlYnKGD5bQPXXKYmAobMt_X9CDl9XMlxEmbL0twZrtC5ALTzuC1tc2fiY8Rb256Q7s3A1wPce6ojbok_iH-SzUhNtpODj9CCiuzm2uoJ0N--VGrskOuyxz95ELthBoXN2grr68ipl0PKlnUDL0r9DT7r9Q0cIf2CfLozCyuoGIjWIZ-oYz0WKWuxtWIbTCdO7v2CFVtqgpdpB1pvmB1bUYASSvsIqWt4GKsFtMtnj1cdppbtLKJP3aU9_muLqzkNmyGuj2ch2lu0ZpiEHHJ7XGbLCBqFyfair8AdsNYPQKi6iJ0TQjhsaQuNRlinrQerTqPpX1EgSVdi8B9ONLlqOMzRPdlQPiaMXnitI-apmIFENG4chYNda_EzNsAlD5M6iqMM8XW9d1HB1oLGYtX0q1S-xfoUDqyMZkEJILhrRdzHaeOI1EMCR9_WHk-zeykslBOSjGyAilhxJITKY7t57kK3roOZVdpeFKIebs7CNt4_dv96TVxrmn0dTQG3p905Q68Xurn0y62AeDqOFjDF3E6nsNel_YdTF7AkqmvqQXfU8Pz40aI60dQQ==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-05T14:00:00.000Z", "utc_arrival": "2023-06-05T12:00:00.000Z", "local_departure": "2023-06-05T10:40:00.000Z", "utc_departure": "2023-06-05T08:40:00.000Z"}, {"id": "0b770a224c4400001cdf0063_0|0a220b774c4700009310bb78_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 648.715444, "distance": 1975.87, "duration": {"departure": 12600, "return": 11400, "total": 24000}, "price": 188730.0014, "conversion": {"EUR": 494.049164, "HUF": 188730.0014}, "fare": {"adults": 94365, "children": 97720.64, "infants": 97720.64}, "bags_price": {"1": 76.454, "2": 152.908}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 2}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224c4400001cdf0063_0", "combination_id": "0b770a224c4400001cdf0063", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "HIREG", "fare_category": "M", "fare_classes": "H", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-16T19:45:00.000Z", "utc_arrival": "2023-06-16T17:45:00.000Z", "local_departure": "2023-06-16T16:15:00.000Z", "utc_departure": "2023-06-16T14:15:00.000Z"}, {"id": "0a220b774c4700009310bb78_0", "combination_id": "0a220b774c4700009310bb78", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-19T10:15:00.000Z", "utc_arrival": "2023-06-19T08:15:00.000Z", "local_departure": "2023-06-19T07:05:00.000Z", "utc_departure": "2023-06-19T05:05:00.000Z"}], "booking_token": "E6fK-TcAYQqD7jyFoDY1-7v3CXl7sxFE22A4GrsShpKmt4f1j7tz1L2a5alRxGa-MYMU_HJ4o5fIeP-4f0Q4L27ZCZgs5fdhkQ7fQm9xIQiXeBpUGxvDx5mealizcunmGcwlbnwoO-J9utGpcC__Br7f4ztcNnVV4T9_sj_Xb6BVUBiy-AW8VnyrfpU-2aMrYH7xq1hKTQbwprcGWf9z1-89A9v29FuVGikSGUKzkJZLjW_N73yAqhmMUHKFw9tD2I5G2b6kK3zh55UirziMXmdd_XXcZZuQpb96cHHaU5OM7udp6Uym_sdMuymVj7VtK7IMPkdm3aI_BaEbWfI8SFGHSDX6bN-hv0B6CXWjDOsib9xz8OPK3WRwGxw51IbF6JMx2m9IOOEYh1m9xUFyuOBHWEmQzci51rT9I9roj46S2SrBwo8UqXBlKa1MGOgU0n0gqnKJZmw2un7-C4YgVQ0sQtJLkNV85KpnoM8GrajrcYLXDXrA3Q7i8lsdh4JCe7WLvXtKljB5HAjo5sboQ6WtY2IhTQeNOHAdrl1E6EWRxMhj8Ta2uIi8H3Qd_wz87A22MwnCZgyPHoPSb0rKl-Tj4DpI3G7urlVSb-Lvnga5ogjZ9glxotobgHrBHOEHqvj6A9mVh8cm8rwFK4l9XOK-qPFc6evd2QpCnRdzjAxCzH7exizMoL-5Tv0bToFbrxdsGUQcdmQWWSDhuHGXaHvfX83l_xAPBQKVOS1X4AjVQ8ghlRkHsnOuswDmGI0ASGqj1jzGMIRMv1McutfrdRjvBs3Ia224mjLPAeICD5mZ9tk7gtOt1kgoYBCx5rc8K", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c4400001cdf0063_0%7C0a220b774c4700009310bb78_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=E6fK-TcAYQqD7jyFoDY1-7v3CXl7sxFE22A4GrsShpKmt4f1j7tz1L2a5alRxGa-MYMU_HJ4o5fIeP-4f0Q4L27ZCZgs5fdhkQ7fQm9xIQiXeBpUGxvDx5mealizcunmGcwlbnwoO-J9utGpcC__Br7f4ztcNnVV4T9_sj_Xb6BVUBiy-AW8VnyrfpU-2aMrYH7xq1hKTQbwprcGWf9z1-89A9v29FuVGikSGUKzkJZLjW_N73yAqhmMUHKFw9tD2I5G2b6kK3zh55UirziMXmdd_XXcZZuQpb96cHHaU5OM7udp6Uym_sdMuymVj7VtK7IMPkdm3aI_BaEbWfI8SFGHSDX6bN-hv0B6CXWjDOsib9xz8OPK3WRwGxw51IbF6JMx2m9IOOEYh1m9xUFyuOBHWEmQzci51rT9I9roj46S2SrBwo8UqXBlKa1MGOgU0n0gqnKJZmw2un7-C4YgVQ0sQtJLkNV85KpnoM8GrajrcYLXDXrA3Q7i8lsdh4JCe7WLvXtKljB5HAjo5sboQ6WtY2IhTQeNOHAdrl1E6EWRxMhj8Ta2uIi8H3Qd_wz87A22MwnCZgyPHoPSb0rKl-Tj4DpI3G7urlVSb-Lvnga5ogjZ9glxotobgHrBHOEHqvj6A9mVh8cm8rwFK4l9XOK-qPFc6evd2QpCnRdzjAxCzH7exizMoL-5Tv0bToFbrxdsGUQcdmQWWSDhuHGXaHvfX83l_xAPBQKVOS1X4AjVQ8ghlRkHsnOuswDmGI0ASGqj1jzGMIRMv1McutfrdRjvBs3Ia224mjLPAeICD5mZ9tk7gtOt1kgoYBCx5rc8K", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-16T19:45:00.000Z", "utc_arrival": "2023-06-16T17:45:00.000Z", "local_departure": "2023-06-16T16:15:00.000Z", "utc_departure": "2023-06-16T14:15:00.000Z"}, {"id": "0b770a224c3d0000866dbf36_0|0a220b774c400000ebc98d9f_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 650.804158, "distance": 1975.87, "duration": {"departure": 12600, "return": 11700, "total": 24300}, "price": 189018.563, "conversion": {"EUR": 494.804548, "HUF": 189018.563}, "fare": {"adults": 94509.28, "children": 94509.28, "infants": 94509.28}, "bags_price": {"1": 107.8, "2": 215.6}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 439, "hold_height": 149, "hold_length": 171, "hold_weight": 20, "hold_width": 119, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 2}, "airlines": ["W6"], "route": [{"id": "0b770a224c3d0000866dbf36_0", "combination_id": "0b770a224c3d0000866dbf36", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "KREG", "fare_category": "M", "fare_classes": "K", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-09T20:45:00.000Z", "utc_arrival": "2023-06-09T18:45:00.000Z", "local_departure": "2023-06-09T17:15:00.000Z", "utc_departure": "2023-06-09T15:15:00.000Z"}, {"id": "0a220b774c400000ebc98d9f_0", "combination_id": "0a220b774c400000ebc98d9f", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "JREG", "fare_category": "M", "fare_classes": "J", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-12T23:45:00.000Z", "utc_arrival": "2023-06-12T21:45:00.000Z", "local_departure": "2023-06-12T20:30:00.000Z", "utc_departure": "2023-06-12T18:30:00.000Z"}], "booking_token": "E7yMVGMJPCfEMid4iIy1TwBfVd3DkM56FwBnRUK6ylkHQ-QjEuKrF8_Tw1IVIP7DJihaoq9r7KC7yTbmsbXBRe6MXVVQVSWvYmlZJjzyU1be36Jd4M1iU5cIWWZWD-f40K390f6TwfOZLb3Ygthglxdow6WD0PfiLHq_4RONWpbO7_WGNZneN1i1Jv-rCXhiu2mfWMlWcpH_aflXq1jzssdnZ5sS9XZTtXSzTMM_cjUlmabpIpu3dXKINAD-BWr_RJer3ZqvWS_mbas3cKSdkxiRlfIhR02T1rBeERAXtCQSMx0xNd6x9NWpWgGGJdu2af9gDVzMr3O09zepQzQ6jQFy7TfnGvQ0OFJl45KHJ1QOpaD4ZwyJOz1-sjMvNEoBqgcZK4AidV0syZvOxWD2ka68nP80RBBwdzlEUtQj5OlJ0U5pDBgz_vZ28heMjOq6GVUYv9kBkYskHHcDt9Mv-9Ily-XKMdwhBMMtNuKXdulaC5bP5DqVfxLoUaVsJaAVAGPFtUqNBXIanVXf-pX98TC2ar1PvapGKE9BUHP7NQYJ6IGgigjJ_mR01NjLwIiaQsR5B43M_-f9GYUqhAqjXhqMZx2Nusqor3jtIxSDTqd61QKZtoPbivhhA_emsJsoC_wD7J56FLolO-kGRqQPLHz5c7TQwA1uCcTm1wFTqZi7NgooXfQ7KLrN1O_cJ3kWRcGcKCfw7wjzQVPpPLr7Lch0uvat1OQjsed_Wf4LngGKxbWd9G8G2N2fiorb6Vnr8UuZ4hpSYN_-7e-6PB7T8UA==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c3d0000866dbf36_0%7C0a220b774c400000ebc98d9f_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=E7yMVGMJPCfEMid4iIy1TwBfVd3DkM56FwBnRUK6ylkHQ-QjEuKrF8_Tw1IVIP7DJihaoq9r7KC7yTbmsbXBRe6MXVVQVSWvYmlZJjzyU1be36Jd4M1iU5cIWWZWD-f40K390f6TwfOZLb3Ygthglxdow6WD0PfiLHq_4RONWpbO7_WGNZneN1i1Jv-rCXhiu2mfWMlWcpH_aflXq1jzssdnZ5sS9XZTtXSzTMM_cjUlmabpIpu3dXKINAD-BWr_RJer3ZqvWS_mbas3cKSdkxiRlfIhR02T1rBeERAXtCQSMx0xNd6x9NWpWgGGJdu2af9gDVzMr3O09zepQzQ6jQFy7TfnGvQ0OFJl45KHJ1QOpaD4ZwyJOz1-sjMvNEoBqgcZK4AidV0syZvOxWD2ka68nP80RBBwdzlEUtQj5OlJ0U5pDBgz_vZ28heMjOq6GVUYv9kBkYskHHcDt9Mv-9Ily-XKMdwhBMMtNuKXdulaC5bP5DqVfxLoUaVsJaAVAGPFtUqNBXIanVXf-pX98TC2ar1PvapGKE9BUHP7NQYJ6IGgigjJ_mR01NjLwIiaQsR5B43M_-f9GYUqhAqjXhqMZx2Nusqor3jtIxSDTqd61QKZtoPbivhhA_emsJsoC_wD7J56FLolO-kGRqQPLHz5c7TQwA1uCcTm1wFTqZi7NgooXfQ7KLrN1O_cJ3kWRcGcKCfw7wjzQVPpPLr7Lch0uvat1OQjsed_Wf4LngGKxbWd9G8G2N2fiorb6Vnr8UuZ4hpSYN_-7e-6PB7T8UA==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-09T20:45:00.000Z", "utc_arrival": "2023-06-09T18:45:00.000Z", "local_departure": "2023-06-09T17:15:00.000Z", "utc_departure": "2023-06-09T15:15:00.000Z"}, {"id": "0b770a224c4b00004d10476b_0|0a220b774c4f0000a7608cfc_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 651.391876, "distance": 1975.87, "duration": {"departure": 12600, "return": 11400, "total": 24000}, "price": 189752.4158, "conversion": {"EUR": 496.725596, "HUF": 189752.4158}, "fare": {"adults": 94876.21, "children": 94876.21, "infants": 94876.21}, "bags_price": {"1": 103.11, "2": 206.206}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 3}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224c4b00004d10476b_0", "combination_id": "0b770a224c4b00004d10476b", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IJREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-23T19:45:00.000Z", "utc_arrival": "2023-06-23T17:45:00.000Z", "local_departure": "2023-06-23T16:15:00.000Z", "utc_departure": "2023-06-23T14:15:00.000Z"}, {"id": "0a220b774c4f0000a7608cfc_0", "combination_id": "0a220b774c4f0000a7608cfc", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-27T14:05:00.000Z", "utc_arrival": "2023-06-27T12:05:00.000Z", "local_departure": "2023-06-27T10:55:00.000Z", "utc_departure": "2023-06-27T08:55:00.000Z"}], "booking_token": "ECkh2xLYdAVOfzCeHdQB8sC_fbuoTHRnrsJ02xR1qf7bmOo0FHHRcPv0tjrl6Wcq2PFuazJDsT_ERdyxoTkHCbRPPj0ZKl2NM1d163Afw5ZQMZyB1Wv6_Rs79_EEVNZHNjfovmVL7LmLitFqdICcPbrasF78PaynZdoy0KZTIY8oBpKSKGiAbyLWH56QAITUCiOA--TtXnc6fXl3WdN-NJaKei3uCYTEZFyV0A11b_AOJdGdACysWdqSxAMvljdZZ1AWAEhndCaIGxTXdzY8bQSWpU45LuABcUVExlXsGwO-kzyzY46vfIGn5xwvjxJdXjpeTscOaPs7nChhBTB0iQTWcT6EoQvIJD9mAD9EhFgYRsqIA9mXB7itnuOQ_tDqE2axS1x2QtPLkeCG_mzQvImOVL0g1ofZl44C6MAAt9McmR6PWFApJRfClB35OUj3vrIiPsSqGvgBzcjO5_09bDxhUzzg8xdCpju_zMjrcHKY67j3JDnjMVHJlzHGwY798dby8SUWpm9cgee08rF-RJO7BkOob8T4xFOXngxtQzMUEVeSl2iMoHyQ_ysMD-3JZF9Co8lcPDsZx4ve7S2VNrxKRCVJfASiwYPj7ahKioQ-ZoC3ydMH5iCdwnjvyKvZL08pZy4d-KAcvViPa3cFvm3NR-W9Dlv-6vF-07wtRn4oMIPmnvJI9PJV_6HnbHUcFUd7sP9WPdBl61sjRwcWogwff1V9cEyRHlZuEDYgDdM7CiqZALUHJeaH_7nKpAT9ilJdOar3UJTVCqRvTsMHlhNBSXMKwsrbuWE10MaqNuhM=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c4b00004d10476b_0%7C0a220b774c4f0000a7608cfc_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=ECkh2xLYdAVOfzCeHdQB8sC_fbuoTHRnrsJ02xR1qf7bmOo0FHHRcPv0tjrl6Wcq2PFuazJDsT_ERdyxoTkHCbRPPj0ZKl2NM1d163Afw5ZQMZyB1Wv6_Rs79_EEVNZHNjfovmVL7LmLitFqdICcPbrasF78PaynZdoy0KZTIY8oBpKSKGiAbyLWH56QAITUCiOA--TtXnc6fXl3WdN-NJaKei3uCYTEZFyV0A11b_AOJdGdACysWdqSxAMvljdZZ1AWAEhndCaIGxTXdzY8bQSWpU45LuABcUVExlXsGwO-kzyzY46vfIGn5xwvjxJdXjpeTscOaPs7nChhBTB0iQTWcT6EoQvIJD9mAD9EhFgYRsqIA9mXB7itnuOQ_tDqE2axS1x2QtPLkeCG_mzQvImOVL0g1ofZl44C6MAAt9McmR6PWFApJRfClB35OUj3vrIiPsSqGvgBzcjO5_09bDxhUzzg8xdCpju_zMjrcHKY67j3JDnjMVHJlzHGwY798dby8SUWpm9cgee08rF-RJO7BkOob8T4xFOXngxtQzMUEVeSl2iMoHyQ_ysMD-3JZF9Co8lcPDsZx4ve7S2VNrxKRCVJfASiwYPj7ahKioQ-ZoC3ydMH5iCdwnjvyKvZL08pZy4d-KAcvViPa3cFvm3NR-W9Dlv-6vF-07wtRn4oMIPmnvJI9PJV_6HnbHUcFUd7sP9WPdBl61sjRwcWogwff1V9cEyRHlZuEDYgDdM7CiqZALUHJeaH_7nKpAT9ilJdOar3UJTVCqRvTsMHlhNBSXMKwsrbuWE10MaqNuhM=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-23T19:45:00.000Z", "utc_arrival": "2023-06-23T17:45:00.000Z", "local_departure": "2023-06-23T16:15:00.000Z", "utc_departure": "2023-06-23T14:15:00.000Z"}, {"id": "0b770a224c3d0000866dbf36_0|0a220b774c41000001ce5e6c_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 652.126129, "distance": 1975.87, "duration": {"departure": 12600, "return": 11400, "total": 24000}, "price": 190032.9053, "conversion": {"EUR": 497.459849, "HUF": 190032.9053}, "fare": {"adults": 95016.45, "children": 95016.45, "infants": 95016.45}, "bags_price": {"1": 95.186, "2": 190.372}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 2}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224c3d0000866dbf36_0", "combination_id": "0b770a224c3d0000866dbf36", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "KREG", "fare_category": "M", "fare_classes": "K", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-09T20:45:00.000Z", "utc_arrival": "2023-06-09T18:45:00.000Z", "local_departure": "2023-06-09T17:15:00.000Z", "utc_departure": "2023-06-09T15:15:00.000Z"}, {"id": "0a220b774c41000001ce5e6c_0", "combination_id": "0a220b774c41000001ce5e6c", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-13T14:05:00.000Z", "utc_arrival": "2023-06-13T12:05:00.000Z", "local_departure": "2023-06-13T10:55:00.000Z", "utc_departure": "2023-06-13T08:55:00.000Z"}], "booking_token": "EB1Rfv7l4Ko-dIxT6yLJ64ObSvMZPyBd24H_R714nm1j2ivItqR2VWs7eEzPRRNuSrNVUIE-1uDDWvfG0R049HhRlkk8NYK6N4usm28UZoJvryI-pDe8XjPSoFbLwzOoHGNpdSXr10z0axs5twNH25Eo4NW9EedFHdSi9KAI2IQDPipCwTKPbwEj0-iKZ9u-30NMuP-1uJyr5FNY3Mg8dC__MvQNfRjoFgzudg9502yHRu7_GR2GlYIyVJQIqrDcNOjA8ZixY8jBVJW0Ejyru4ZIK1P-IXAfEF7aYGqWMhezN0BQaWsyJtrfZaDOUvlEiv6n909Vt2PSxlOUrwSXulskUaPBNDavPyy__MqbVGaiuZpT6T1Ik5QveoW2Ze5x2HSbKHlPuV6XXqRp2UJQkHeaQM4VbRE2D-v8wseMcM1ZevR4wIXRr1DqXzGRFOwkp0QR-FpOIw2fAdPWLEV-9XoK_a9UaX7EQhrYOyPkkTXoBNknLMJDFwCdqrZXfVoKuK1g_F3Cl185O56r9hBodlHexyZQM9tEKTgLjJWL_mKtRyDkEcBsfzzi8hEECMIU4DYEDx7SqXM40RDECbOpsZ55KW5IqzkmNkydhSHml304I3EvUYr8vRkavSqC471KtkAvADb4QT2CX-yhh0joT3l2_G8GpnSEL3LK8eu8X2gIX1PSKtwUW2KqEelfvSee9BT9Gqkqt-d4RZuuSRBNpU1fooSRg9P8VgCJWhfPUtTa5EmELX6w1SuviaehInqoIM-ajMS752twDc2bToJGUdSThps3_aLfvu3coX8mLf1Q=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c3d0000866dbf36_0%7C0a220b774c41000001ce5e6c_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EB1Rfv7l4Ko-dIxT6yLJ64ObSvMZPyBd24H_R714nm1j2ivItqR2VWs7eEzPRRNuSrNVUIE-1uDDWvfG0R049HhRlkk8NYK6N4usm28UZoJvryI-pDe8XjPSoFbLwzOoHGNpdSXr10z0axs5twNH25Eo4NW9EedFHdSi9KAI2IQDPipCwTKPbwEj0-iKZ9u-30NMuP-1uJyr5FNY3Mg8dC__MvQNfRjoFgzudg9502yHRu7_GR2GlYIyVJQIqrDcNOjA8ZixY8jBVJW0Ejyru4ZIK1P-IXAfEF7aYGqWMhezN0BQaWsyJtrfZaDOUvlEiv6n909Vt2PSxlOUrwSXulskUaPBNDavPyy__MqbVGaiuZpT6T1Ik5QveoW2Ze5x2HSbKHlPuV6XXqRp2UJQkHeaQM4VbRE2D-v8wseMcM1ZevR4wIXRr1DqXzGRFOwkp0QR-FpOIw2fAdPWLEV-9XoK_a9UaX7EQhrYOyPkkTXoBNknLMJDFwCdqrZXfVoKuK1g_F3Cl185O56r9hBodlHexyZQM9tEKTgLjJWL_mKtRyDkEcBsfzzi8hEECMIU4DYEDx7SqXM40RDECbOpsZ55KW5IqzkmNkydhSHml304I3EvUYr8vRkavSqC471KtkAvADb4QT2CX-yhh0joT3l2_G8GpnSEL3LK8eu8X2gIX1PSKtwUW2KqEelfvSee9BT9Gqkqt-d4RZuuSRBNpU1fooSRg9P8VgCJWhfPUtTa5EmELX6w1SuviaehInqoIM-ajMS752twDc2bToJGUdSThps3_aLfvu3coX8mLf1Q=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-09T20:45:00.000Z", "utc_arrival": "2023-06-09T18:45:00.000Z", "local_departure": "2023-06-09T17:15:00.000Z", "utc_departure": "2023-06-09T15:15:00.000Z"}, {"id": "0b770a224c220000d443d632_0|0a220b774c250000060d8840_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 650.872382, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 190572.6472, "conversion": {"EUR": 498.872762, "HUF": 190572.6472}, "fare": {"adults": 95286.32, "children": 95286.32, "infants": 95286.32}, "bags_price": {"1": 74.088, "2": 148.162}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 2}, "airlines": ["FR"], "route": [{"id": "0b770a224c220000d443d632_0", "combination_id": "0b770a224c220000d443d632", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-13T13:25:00.000Z", "utc_arrival": "2023-05-13T11:25:00.000Z", "local_departure": "2023-05-13T10:05:00.000Z", "utc_departure": "2023-05-13T08:05:00.000Z"}, {"id": "0a220b774c250000060d8840_0", "combination_id": "0a220b774c250000060d8840", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-16T14:05:00.000Z", "utc_arrival": "2023-05-16T12:05:00.000Z", "local_departure": "2023-05-16T10:55:00.000Z", "utc_departure": "2023-05-16T08:55:00.000Z"}], "booking_token": "ES4mfW_BAIq-eeI5bz9_G_igB5nSKvzUx6TH2u7wc3DXKUJkc65bmjiFzzfutLKi2AG3A-Iy_sN8gVK5oFytAD7CUsR23M1JH1mJ3xi29WKJxG5yeKV8pXLCqhemh-MFYFsIOHJINdK74fcvnXSojzi9PzeGkJ8AnWi6OcXrzwO9LySYIuiHo4gnzDpwA9q2SZ-S4fzhWGJMHok_FznG4sJke76u3Vuo05w19T8v7LUPfhTSEUPvWQbl92k99khJvJAgITxoJKz479AmODRNRuHcg9soTKdnGA_h9s04RTxzNIonj9Im_rsVFvMeYOcG6smXBpMuQsT09ZsDdLtRaWcKLIUqKWyYn6Um3aNLSNrgkVEoayfnVQmmyM_di5890X-IELvZ_tACMURUt6vcYIkAHPH8HEDZ5by7vkkeTliRGUxikr4V1RRxESh7tn4jQkiUXiZQC6Yq9cg8XFNPjH5loGzDmCyUlzpgBIVOWJSDUR5LZC_qdmPaG9L_DIvNChvyyIfhoE0XJkAgEV2HIOv7myTVw9c2IoY05Q3EAvkDIDvkOotBIbgfIAyaWMzBi3imSROS8Mlyt1v5upzIcZtxNtpv2DahiCi0f0a8DQdbtJm4BMrm_kntr1DU0j_k2UjjlwRiFDe4bJPuKjmDWOhQ6TqYyWSAdcMm5hfJQbQ1mt7BIR78ZPrN5oDT4s5bWZ3O6OFfNehx5rxjB7IYXG9UAzgsBfdICpWEtUGtHMsbpN-ddkOnGIDy4tXNz3s1EboQxQyWY-jRLTbPPnMHS_A==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c220000d443d632_0%7C0a220b774c250000060d8840_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=ES4mfW_BAIq-eeI5bz9_G_igB5nSKvzUx6TH2u7wc3DXKUJkc65bmjiFzzfutLKi2AG3A-Iy_sN8gVK5oFytAD7CUsR23M1JH1mJ3xi29WKJxG5yeKV8pXLCqhemh-MFYFsIOHJINdK74fcvnXSojzi9PzeGkJ8AnWi6OcXrzwO9LySYIuiHo4gnzDpwA9q2SZ-S4fzhWGJMHok_FznG4sJke76u3Vuo05w19T8v7LUPfhTSEUPvWQbl92k99khJvJAgITxoJKz479AmODRNRuHcg9soTKdnGA_h9s04RTxzNIonj9Im_rsVFvMeYOcG6smXBpMuQsT09ZsDdLtRaWcKLIUqKWyYn6Um3aNLSNrgkVEoayfnVQmmyM_di5890X-IELvZ_tACMURUt6vcYIkAHPH8HEDZ5by7vkkeTliRGUxikr4V1RRxESh7tn4jQkiUXiZQC6Yq9cg8XFNPjH5loGzDmCyUlzpgBIVOWJSDUR5LZC_qdmPaG9L_DIvNChvyyIfhoE0XJkAgEV2HIOv7myTVw9c2IoY05Q3EAvkDIDvkOotBIbgfIAyaWMzBi3imSROS8Mlyt1v5upzIcZtxNtpv2DahiCi0f0a8DQdbtJm4BMrm_kntr1DU0j_k2UjjlwRiFDe4bJPuKjmDWOhQ6TqYyWSAdcMm5hfJQbQ1mt7BIR78ZPrN5oDT4s5bWZ3O6OFfNehx5rxjB7IYXG9UAzgsBfdICpWEtUGtHMsbpN-ddkOnGIDy4tXNz3s1EboQxQyWY-jRLTbPPnMHS_A==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-13T13:25:00.000Z", "utc_arrival": "2023-05-13T11:25:00.000Z", "local_departure": "2023-05-13T10:05:00.000Z", "utc_departure": "2023-05-13T08:05:00.000Z"}, {"id": "0b770a224c4b0000ee8a8a37_0|0a220b774c4f0000a7608cfc_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 649.585223, "distance": 1975.87, "duration": {"departure": 11700, "return": 11400, "total": 23100}, "price": 190590.2849, "conversion": {"EUR": 498.918933, "HUF": 190590.2849}, "fare": {"adults": 95295.14, "children": 95295.14, "infants": 95295.14}, "bags_price": {"1": 76.986, "2": 163.772}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 158, "hold_height": 52, "hold_length": 78, "hold_weight": 20, "hold_width": 28, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 3, "personal_item_width": 15}, "availability": {"seats": 3}, "airlines": ["FR", "IB"], "route": [{"id": "0b770a224c4b0000ee8a8a37_0", "combination_id": "0b770a224c4b0000ee8a8a37", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "IB", "flight_no": 3279, "operating_carrier": "IB", "operating_flight_no": "3279", "fare_basis": "QWNNAOB4", "fare_category": "M", "fare_classes": "Q", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-23T18:50:00.000Z", "utc_arrival": "2023-06-23T16:50:00.000Z", "local_departure": "2023-06-23T15:35:00.000Z", "utc_departure": "2023-06-23T13:35:00.000Z"}, {"id": "0a220b774c4f0000a7608cfc_0", "combination_id": "0a220b774c4f0000a7608cfc", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-27T14:05:00.000Z", "utc_arrival": "2023-06-27T12:05:00.000Z", "local_departure": "2023-06-27T10:55:00.000Z", "utc_departure": "2023-06-27T08:55:00.000Z"}], "booking_token": "E5o0StYEk_Qa-WKvrwNAixqzGQcOm14BNxCcaiY1kPxCupbd5JUgdik7OECU3PjnyePFhT6_y10dAY7QMzCDXM3PVyi876bkfQMzeTgalxrc_47k-fslJVMIOD5sBDlWf7l9HaD-j5-MLHHp8pt-dZLADwOUjlOsdPmwuhulLsmHRfIN6H0Yvy8eORorcuUq0mjdOG6rKMIFUIFpekRRHVYrUaaNb8QczSU8Qcv3d9wjkCA3YynPg3QyMn17udh0N_yixOhh769rjTdZdgR4h84R4XS3eMerTFfYn82uXFnh4IN--KtQ30WggTt-pfThYxSCFOfiRbBlRF6GysGh1O0VdEgV8_nNIHaij3TLhWKFp2HCeFE3zrBI8SZJsFKQTpAz1887df5bT8ashpsA1w-XBxQTA0_WyPhmYlfvSyDy87hyXtp-JiVI3xVBKdfe_-1KvgyI05H1RVOLe-QWhhuImucjIOxwMu7DITbZnoUXlhMU1GQdwBXTYtZ-pqn1ytHxMBzc8aIf4xHw91kZ3Bhjidr77zJ5TZG8cE1kV40kD3vV79pBidz7T0mJ7q4CXsvc5TTPaEi5rbObzHFXIf-wFnkQFAJAfBeddM4p7MkvgfWe12HFgvSQeeIkHVoeKNfnhGR2rbz8fVBRI8WacUhmfyYCGMRbomNnRTph62N6f_y9Ac7n9EFc76SlWEeEzdgCSacxs4QgzzytjBA8yZrQCDr7-drDeDlOGfC6x8GLk2g5uJ2lyuYhHEPCEhAULW1TYGUrpkOaq8WBpMXnEpPExUFD2xLvBlMBghXm0oSe5Rl4LI3oTPOxQ8kQwVCaE", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c4b0000ee8a8a37_0%7C0a220b774c4f0000a7608cfc_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=E5o0StYEk_Qa-WKvrwNAixqzGQcOm14BNxCcaiY1kPxCupbd5JUgdik7OECU3PjnyePFhT6_y10dAY7QMzCDXM3PVyi876bkfQMzeTgalxrc_47k-fslJVMIOD5sBDlWf7l9HaD-j5-MLHHp8pt-dZLADwOUjlOsdPmwuhulLsmHRfIN6H0Yvy8eORorcuUq0mjdOG6rKMIFUIFpekRRHVYrUaaNb8QczSU8Qcv3d9wjkCA3YynPg3QyMn17udh0N_yixOhh769rjTdZdgR4h84R4XS3eMerTFfYn82uXFnh4IN--KtQ30WggTt-pfThYxSCFOfiRbBlRF6GysGh1O0VdEgV8_nNIHaij3TLhWKFp2HCeFE3zrBI8SZJsFKQTpAz1887df5bT8ashpsA1w-XBxQTA0_WyPhmYlfvSyDy87hyXtp-JiVI3xVBKdfe_-1KvgyI05H1RVOLe-QWhhuImucjIOxwMu7DITbZnoUXlhMU1GQdwBXTYtZ-pqn1ytHxMBzc8aIf4xHw91kZ3Bhjidr77zJ5TZG8cE1kV40kD3vV79pBidz7T0mJ7q4CXsvc5TTPaEi5rbObzHFXIf-wFnkQFAJAfBeddM4p7MkvgfWe12HFgvSQeeIkHVoeKNfnhGR2rbz8fVBRI8WacUhmfyYCGMRbomNnRTph62N6f_y9Ac7n9EFc76SlWEeEzdgCSacxs4QgzzytjBA8yZrQCDr7-drDeDlOGfC6x8GLk2g5uJ2lyuYhHEPCEhAULW1TYGUrpkOaq8WBpMXnEpPExUFD2xLvBlMBghXm0oSe5Rl4LI3oTPOxQ8kQwVCaE", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-23T18:50:00.000Z", "utc_arrival": "2023-06-23T16:50:00.000Z", "local_departure": "2023-06-23T15:35:00.000Z", "utc_departure": "2023-06-23T13:35:00.000Z"}, {"id": "0b770a224c3d000092cf2d05_0|0a220b774c41000001ce5e6c_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 652.888454, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 191342.7999, "conversion": {"EUR": 500.888834, "HUF": 191342.7999}, "fare": {"adults": 95671.4, "children": 95671.4, "infants": 95671.4}, "bags_price": {"1": 72.744, "2": 145.502}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 2}, "airlines": ["FR"], "route": [{"id": "0b770a224c3d000092cf2d05_0", "combination_id": "0b770a224c3d000092cf2d05", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-09T21:45:00.000Z", "utc_arrival": "2023-06-09T19:45:00.000Z", "local_departure": "2023-06-09T18:25:00.000Z", "utc_departure": "2023-06-09T16:25:00.000Z"}, {"id": "0a220b774c41000001ce5e6c_0", "combination_id": "0a220b774c41000001ce5e6c", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-13T14:05:00.000Z", "utc_arrival": "2023-06-13T12:05:00.000Z", "local_departure": "2023-06-13T10:55:00.000Z", "utc_departure": "2023-06-13T08:55:00.000Z"}], "booking_token": "EJls_cUWu3Ke9EKHj3MBW0MYoKqziYCgMA8KwmumbR64i3IPF4wQvY-YFTM11ciAzCoQ2dQj_LvScGUtkZJLNix4Oj0J9qyCy2KbC2Fs-38T_gsyEdZ4PyrNX7Jf94m0AjXcoxCNvuXK2clyGe5c4fS1ANfyDli00rJ1GDkcyaAK04Hvymlh2yvPzx9r5Ot8zrzyOhpNMg0d_H0_oOfqfwH91ykQOnrkF5qTdtFb1GBbqGf-ZUQVAIWn2eMRwlLP86crEBaxIB_Wa_nZ-EbLqtGmFOZ_cnYppIMyGor6B6d_wOrfvdcX5ZD_JmXkPP8AVLldHbgS86oX5hgHwIs9izy_DrQ33tDrkXjC30dGuBukuQKSUeL4vEIyg4kjptlnp3yRhmlIxHpofLdOe81pkLkqcudZ-wjextGcIbjhQQdjnjYHLyaKnd1WD5EF86Pq9ngH9FKXhD3mAOlsmiAgPZ8oYgWEiqoUlDiEQVt78Cls1XZ1qrEGNlDVBUA1XeRLu_hMmm87WMMyol2HoHSw8Gym6sqi_yeVoBnP_-IuwNGO4Uybyfyj_gYd2xCaA7NoQ735Lo71wA0NVa8jUKsLdyfas_w2WJ8Igmps_eH2yE9xyHYbcD6OY0sK9SA3K9oO0ziSo33jqok5ynwJHRTlK_5_Re9kJvxaNQZqCEjvg-bpljoPq5OzhgbK69p67Nu9taY8Mo_OjnrcyAHREScbQhz8K-AzIh2-bxAysXKJQb_3vaQ76BogVwWPDLOcquhp0", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c3d000092cf2d05_0%7C0a220b774c41000001ce5e6c_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EJls_cUWu3Ke9EKHj3MBW0MYoKqziYCgMA8KwmumbR64i3IPF4wQvY-YFTM11ciAzCoQ2dQj_LvScGUtkZJLNix4Oj0J9qyCy2KbC2Fs-38T_gsyEdZ4PyrNX7Jf94m0AjXcoxCNvuXK2clyGe5c4fS1ANfyDli00rJ1GDkcyaAK04Hvymlh2yvPzx9r5Ot8zrzyOhpNMg0d_H0_oOfqfwH91ykQOnrkF5qTdtFb1GBbqGf-ZUQVAIWn2eMRwlLP86crEBaxIB_Wa_nZ-EbLqtGmFOZ_cnYppIMyGor6B6d_wOrfvdcX5ZD_JmXkPP8AVLldHbgS86oX5hgHwIs9izy_DrQ33tDrkXjC30dGuBukuQKSUeL4vEIyg4kjptlnp3yRhmlIxHpofLdOe81pkLkqcudZ-wjextGcIbjhQQdjnjYHLyaKnd1WD5EF86Pq9ngH9FKXhD3mAOlsmiAgPZ8oYgWEiqoUlDiEQVt78Cls1XZ1qrEGNlDVBUA1XeRLu_hMmm87WMMyol2HoHSw8Gym6sqi_yeVoBnP_-IuwNGO4Uybyfyj_gYd2xCaA7NoQ735Lo71wA0NVa8jUKsLdyfas_w2WJ8Igmps_eH2yE9xyHYbcD6OY0sK9SA3K9oO0ziSo33jqok5ynwJHRTlK_5_Re9kJvxaNQZqCEjvg-bpljoPq5OzhgbK69p67Nu9taY8Mo_OjnrcyAHREScbQhz8K-AzIh2-bxAysXKJQb_3vaQ76BogVwWPDLOcquhp0", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-09T21:45:00.000Z", "utc_arrival": "2023-06-09T19:45:00.000Z", "local_departure": "2023-06-09T18:25:00.000Z", "utc_departure": "2023-06-09T16:25:00.000Z"}, {"id": "0b770a224c4800006d0d7298_0|0a220b774c4b0000d381db8e_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 654.317899, "distance": 1975.87, "duration": {"departure": 12000, "return": 11700, "total": 23700}, "price": 191379.5164, "conversion": {"EUR": 500.984949, "HUF": 191379.5164}, "fare": {"adults": 95689.76, "children": 95689.76, "infants": 95689.76}, "bags_price": {"1": 95.172, "2": 190.344}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 2}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224c4800006d0d7298_0", "combination_id": "0b770a224c4800006d0d7298", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-20T10:15:00.000Z", "utc_arrival": "2023-06-20T08:15:00.000Z", "local_departure": "2023-06-20T06:55:00.000Z", "utc_departure": "2023-06-20T04:55:00.000Z"}, {"id": "0a220b774c4b0000d381db8e_0", "combination_id": "0a220b774c4b0000d381db8e", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "JREG", "fare_category": "M", "fare_classes": "J", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-23T23:45:00.000Z", "utc_arrival": "2023-06-23T21:45:00.000Z", "local_departure": "2023-06-23T20:30:00.000Z", "utc_departure": "2023-06-23T18:30:00.000Z"}], "booking_token": "EgkIf212_dqOafCwbmvMTU23F1wuLAzWsMKHEbRY7yMJzpgpFbYPIdIqMa6a4N4_udlIHF8ZX298O3TBVCM3OGwr6PTkJeFyr3XYO8Yca0RQ6R6YwsMpF2xbczaJiYk_RXrBBPZPiPeCdPjBBnC7UxtCUn7Mv6YFp1zZ4bStnhdwvVe5Vkn9lh0QwkdUQM5wpWqULI8P5rFvW6t5BFS-78o6C0J7wsRNn8kPW3LmWNlg-_6Spl78tJ2h1dQoO5vvOvd-lNvdnBz5KPTxy-ZhY-qo5_BVq9lM472yzShbGTowUxHJPrvwoiWp8vcbUex1Rltx-z5-oFmfIlr1QmEVJN_hJZL_VF2LqHRoLnVqAG7jBZe2xdzdnp36_l4aAhYsAlTZ9Vq4oefvODJlaal5dH_nwLlWNFre9eTmwf6v1gp0_6HTN4bDV9vroXDx2GM4V9lj_Kp12k3P1AuGzAc3LlKDOtx3liK5QheOhGSVzcvBVRySsdOvL2g2ff29wMNyjT1bIqr7swr5jvhx-bBN76IT6XFsPFsh4HqrVvnNJvVpu_jEnL6i4CWjTMRs9laeKwK0qBL2CJTVsWkUB5VlKGIgZoqKrZczfKhpD8LaPjAMwAyMsUGcAkyju8CGQUJZUyjO4534vZxTGoK9FX4NB0vbZfH9p9Jt5JeQsu9Lhwd0K_XyPjGhg5VBYCqHOagRLnVj9U0vJYndFgjfBtT-CDVJjIc34EzjtF8TGxuIZvA2a9wzlRhzD2DhhaDL6c4bh_PprFU7XZHqzTRemEr_cPg==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c4800006d0d7298_0%7C0a220b774c4b0000d381db8e_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EgkIf212_dqOafCwbmvMTU23F1wuLAzWsMKHEbRY7yMJzpgpFbYPIdIqMa6a4N4_udlIHF8ZX298O3TBVCM3OGwr6PTkJeFyr3XYO8Yca0RQ6R6YwsMpF2xbczaJiYk_RXrBBPZPiPeCdPjBBnC7UxtCUn7Mv6YFp1zZ4bStnhdwvVe5Vkn9lh0QwkdUQM5wpWqULI8P5rFvW6t5BFS-78o6C0J7wsRNn8kPW3LmWNlg-_6Spl78tJ2h1dQoO5vvOvd-lNvdnBz5KPTxy-ZhY-qo5_BVq9lM472yzShbGTowUxHJPrvwoiWp8vcbUex1Rltx-z5-oFmfIlr1QmEVJN_hJZL_VF2LqHRoLnVqAG7jBZe2xdzdnp36_l4aAhYsAlTZ9Vq4oefvODJlaal5dH_nwLlWNFre9eTmwf6v1gp0_6HTN4bDV9vroXDx2GM4V9lj_Kp12k3P1AuGzAc3LlKDOtx3liK5QheOhGSVzcvBVRySsdOvL2g2ff29wMNyjT1bIqr7swr5jvhx-bBN76IT6XFsPFsh4HqrVvnNJvVpu_jEnL6i4CWjTMRs9laeKwK0qBL2CJTVsWkUB5VlKGIgZoqKrZczfKhpD8LaPjAMwAyMsUGcAkyju8CGQUJZUyjO4534vZxTGoK9FX4NB0vbZfH9p9Jt5JeQsu9Lhwd0K_XyPjGhg5VBYCqHOagRLnVj9U0vJYndFgjfBtT-CDVJjIc34EzjtF8TGxuIZvA2a9wzlRhzD2DhhaDL6c4bh_PprFU7XZHqzTRemEr_cPg==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-20T10:15:00.000Z", "utc_arrival": "2023-06-20T08:15:00.000Z", "local_departure": "2023-06-20T06:55:00.000Z", "utc_departure": "2023-06-20T04:55:00.000Z"}, {"id": "0b770a224c4a0000c81c2b63_0|0a220b774c4e000024b82646_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 651.841729, "distance": 1975.87, "duration": {"departure": 11700, "return": 11400, "total": 23100}, "price": 191452.2849, "conversion": {"EUR": 501.175439, "HUF": 191452.2849}, "fare": {"adults": 95726.14, "children": 95726.14, "infants": 95726.14}, "bags_price": {"1": 76.986, "2": 163.772}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 158, "hold_height": 52, "hold_length": 78, "hold_weight": 20, "hold_width": 28, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 3, "personal_item_width": 15}, "availability": {"seats": 3}, "airlines": ["FR", "IB"], "route": [{"id": "0b770a224c4a0000c81c2b63_0", "combination_id": "0b770a224c4a0000c81c2b63", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "IB", "flight_no": 3279, "operating_carrier": "IB", "operating_flight_no": "3279", "fare_basis": "ODNNAOB4", "fare_category": "M", "fare_classes": "O", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-22T18:50:00.000Z", "utc_arrival": "2023-06-22T16:50:00.000Z", "local_departure": "2023-06-22T15:35:00.000Z", "utc_departure": "2023-06-22T13:35:00.000Z"}, {"id": "0a220b774c4e000024b82646_0", "combination_id": "0a220b774c4e000024b82646", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-26T10:15:00.000Z", "utc_arrival": "2023-06-26T08:15:00.000Z", "local_departure": "2023-06-26T07:05:00.000Z", "utc_departure": "2023-06-26T05:05:00.000Z"}], "booking_token": "EsJ5vwbQfo1LDaQvlVApdT8Uc7gN7gonc2RO1i2SbNmOQvleT9Xb2u4QQuNGvSrGkpI-z1extCt-79ZwePBNTCMiq1M49eKDulTQDEi_5PTcfhpGHOREsSe4AUn0IjBVlsHBlrophIq1a1Z4mxFYTc6LIHRKVF-jKTjDHHaPynSA9tr2KDJ-zde_0YY6sc1_G4_ltBRDw07kFihJQQULPsPvXZsU4mwwb4oEgdpfY0kmynsodHvA3SZ5_Byaw6_TW4MnYxho1ej4AE387CAAGwvpNlgIx9Skq0LM-uJnywLojLGARP2-Fr9dmaekK8XyVYQgxQEB6VjfhNhDmI3jnvxb1WsJsO22_f0RPKTX0qkziLRvRDmh2ywHEXDLGUFbXes_t79RPNZf_xpfTvEqFsEBWdsglKieC-ZvG6z2jypJny9bTa4sAgJpFP2ozZfiDEdO1n4Qhziy8H2kIISBF5GESRKcUgGDlmX0ki0_9DZ7MiZiv93xhLi51ZIjJ4cLEWwcX6gq5_pi9r-hgNXhwoLJh-dxxEgEIhFZxWCeOVQ45o7Fio3PeV1sttJJH8lSkuLCNuPuNBjavAbMKyEbC8glUQ4O7u-GJHZMgFNBqgNQ4utwB_QunFxGN9rZiMfrw-YgojEpjcLCyOXqIva8xTUwMm6n9kmPITnuave-LhJR2VYi3TpdTKa2fOhqNXWfZc-xM_em6KLM4UmeUSAj3v8_8LbeW_7xPDsqlSJUWz5v3ZgOWaFh1OP7FUA3ibd-b5eUxabotjKbh_4NRs7pa0vBsuEZZ048v5nqENR8iNEil9w-Bk62ySnclM3Ju_knI", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c4a0000c81c2b63_0%7C0a220b774c4e000024b82646_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EsJ5vwbQfo1LDaQvlVApdT8Uc7gN7gonc2RO1i2SbNmOQvleT9Xb2u4QQuNGvSrGkpI-z1extCt-79ZwePBNTCMiq1M49eKDulTQDEi_5PTcfhpGHOREsSe4AUn0IjBVlsHBlrophIq1a1Z4mxFYTc6LIHRKVF-jKTjDHHaPynSA9tr2KDJ-zde_0YY6sc1_G4_ltBRDw07kFihJQQULPsPvXZsU4mwwb4oEgdpfY0kmynsodHvA3SZ5_Byaw6_TW4MnYxho1ej4AE387CAAGwvpNlgIx9Skq0LM-uJnywLojLGARP2-Fr9dmaekK8XyVYQgxQEB6VjfhNhDmI3jnvxb1WsJsO22_f0RPKTX0qkziLRvRDmh2ywHEXDLGUFbXes_t79RPNZf_xpfTvEqFsEBWdsglKieC-ZvG6z2jypJny9bTa4sAgJpFP2ozZfiDEdO1n4Qhziy8H2kIISBF5GESRKcUgGDlmX0ki0_9DZ7MiZiv93xhLi51ZIjJ4cLEWwcX6gq5_pi9r-hgNXhwoLJh-dxxEgEIhFZxWCeOVQ45o7Fio3PeV1sttJJH8lSkuLCNuPuNBjavAbMKyEbC8glUQ4O7u-GJHZMgFNBqgNQ4utwB_QunFxGN9rZiMfrw-YgojEpjcLCyOXqIva8xTUwMm6n9kmPITnuave-LhJR2VYi3TpdTKa2fOhqNXWfZc-xM_em6KLM4UmeUSAj3v8_8LbeW_7xPDsqlSJUWz5v3ZgOWaFh1OP7FUA3ibd-b5eUxabotjKbh_4NRs7pa0vBsuEZZ048v5nqENR8iNEil9w-Bk62ySnclM3Ju_knI", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-22T18:50:00.000Z", "utc_arrival": "2023-06-22T16:50:00.000Z", "local_departure": "2023-06-22T15:35:00.000Z", "utc_departure": "2023-06-22T13:35:00.000Z"}, {"id": "0b770a224c390000dc0e5ade_0|0a220b774c3c00005d56eab0_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 655.159674, "distance": 1975.87, "duration": {"departure": 12000, "return": 11700, "total": 23700}, "price": 191701.08, "conversion": {"EUR": 501.826724, "HUF": 191701.08}, "fare": {"adults": 95850.54, "children": 98931.36, "infants": 98931.36}, "bags_price": {"1": 89.768, "2": 179.55}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 6}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224c390000dc0e5ade_0", "combination_id": "0b770a224c390000dc0e5ade", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-05T14:00:00.000Z", "utc_arrival": "2023-06-05T12:00:00.000Z", "local_departure": "2023-06-05T10:40:00.000Z", "utc_departure": "2023-06-05T08:40:00.000Z"}, {"id": "0a220b774c3c00005d56eab0_0", "combination_id": "0a220b774c3c00005d56eab0", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-09T01:15:00.000Z", "utc_arrival": "2023-06-08T23:15:00.000Z", "local_departure": "2023-06-08T22:00:00.000Z", "utc_departure": "2023-06-08T20:00:00.000Z"}], "booking_token": "E0U62uaDTmp374TsnvF5uo1Fen6tr_mxyXPSprGl76j6ouCpLXryP2riowxl1LUQdWoeNtzXV8b62-8b3Klyg-aU7vCp5BCiQ1MQiTbKGc1MRdcGpBL4Gaf2ECzrK9hmwLhlZn5T1z6CvuHOvqCsH_t7Gabc0D8yWfm-_ejgGbJZfda706ZS7IhmY3DlyeBnYashBtDnlERU_P9S9N0m-H2WAquoI4zBYi3aB9D34lpcSKfZi1moe0qyn6-UnnU_ut7CuD63fCRy75bBvKZf_7AgNTdPpSggwy0lz-e3EQsrmMpcgTShpOlv2VDlK8uH2VcNmHGFYN_-8bNpmyq7iEgNYPpqxi73_pjUfE3DLSoN5fNRXY4HyE7hB5xesgj0dXWwMP3m6PRyhqS3ua4aHgTL8fQg8LXMdU8oma9ZMOCfUOEUSddJUVA7KXHykHbgDd5yziKb_SrcEIziVz6KEjjuvUjjuJLZPZPh8slvm20D5Kw7TOjA9bei2VXlE19-NmO3lO-RzIe3shOGd4a1_IrfnmEmTjbPGFubYh8JiwRa5MHhb3ynltW207A-mRURA0uUxK1qyrmOrhf-8JsM4mn7pLxUynomgXTjpLyVnh8Cl4GcJezzSt-TEf16JA3k5md05hD7ZrJoVTZa8XHDoY1mcy8SX8y3WK8p9g62_AOEdGYoJMOtfMVtSL6Zb49JharHbCiJ_slfSnvjkTYvNpRLOfHriWFbRQQVKcwzT5xtOcpPavF1uVf6zCyRMTjdcb6KyxEE6rbw_qxACZfwoYA==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c390000dc0e5ade_0%7C0a220b774c3c00005d56eab0_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=E0U62uaDTmp374TsnvF5uo1Fen6tr_mxyXPSprGl76j6ouCpLXryP2riowxl1LUQdWoeNtzXV8b62-8b3Klyg-aU7vCp5BCiQ1MQiTbKGc1MRdcGpBL4Gaf2ECzrK9hmwLhlZn5T1z6CvuHOvqCsH_t7Gabc0D8yWfm-_ejgGbJZfda706ZS7IhmY3DlyeBnYashBtDnlERU_P9S9N0m-H2WAquoI4zBYi3aB9D34lpcSKfZi1moe0qyn6-UnnU_ut7CuD63fCRy75bBvKZf_7AgNTdPpSggwy0lz-e3EQsrmMpcgTShpOlv2VDlK8uH2VcNmHGFYN_-8bNpmyq7iEgNYPpqxi73_pjUfE3DLSoN5fNRXY4HyE7hB5xesgj0dXWwMP3m6PRyhqS3ua4aHgTL8fQg8LXMdU8oma9ZMOCfUOEUSddJUVA7KXHykHbgDd5yziKb_SrcEIziVz6KEjjuvUjjuJLZPZPh8slvm20D5Kw7TOjA9bei2VXlE19-NmO3lO-RzIe3shOGd4a1_IrfnmEmTjbPGFubYh8JiwRa5MHhb3ynltW207A-mRURA0uUxK1qyrmOrhf-8JsM4mn7pLxUynomgXTjpLyVnh8Cl4GcJezzSt-TEf16JA3k5md05hD7ZrJoVTZa8XHDoY1mcy8SX8y3WK8p9g62_AOEdGYoJMOtfMVtSL6Zb49JharHbCiJ_slfSnvjkTYvNpRLOfHriWFbRQQVKcwzT5xtOcpPavF1uVf6zCyRMTjdcb6KyxEE6rbw_qxACZfwoYA==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-05T14:00:00.000Z", "utc_arrival": "2023-06-05T12:00:00.000Z", "local_departure": "2023-06-05T10:40:00.000Z", "utc_departure": "2023-06-05T08:40:00.000Z"}, {"id": "0b770a224c16000010748fcb_0|0a220b774c1a0000629e77ea_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 663.390481, "distance": 1975.87, "duration": {"departure": 12600, "return": 12900, "total": 25500}, "price": 191789.2574, "conversion": {"EUR": 502.057551, "HUF": 191789.2574}, "fare": {"adults": 95894.63, "children": 95894.63, "infants": 95894.63}, "bags_price": {"1": 110.432, "2": 220.878}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 439, "hold_height": 149, "hold_length": 171, "hold_weight": 20, "hold_width": 119, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 2}, "airlines": ["W6"], "route": [{"id": "0b770a224c16000010748fcb_0", "combination_id": "0b770a224c16000010748fcb", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "JKREG", "fare_category": "M", "fare_classes": "J", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-01T19:45:00.000Z", "utc_arrival": "2023-05-01T17:45:00.000Z", "local_departure": "2023-05-01T16:15:00.000Z", "utc_departure": "2023-05-01T14:15:00.000Z"}, {"id": "0a220b774c1a0000629e77ea_0", "combination_id": "0a220b774c1a0000629e77ea", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "JREG", "fare_category": "M", "fare_classes": "J", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-06T00:05:00.000Z", "utc_arrival": "2023-05-05T22:05:00.000Z", "local_departure": "2023-05-05T20:30:00.000Z", "utc_departure": "2023-05-05T18:30:00.000Z"}], "booking_token": "EwKK9bjvnmuX6KYtPYDfJmDPY-PpSGD8dpJZc4MK1gj4j1dx59HuLM-MUcYJ8c-jlgI46RWQftIO4koAX7hV7N-iescCeL3UP_c3qcBtm7lOoULF5R0BU5-ZLSHrsWjqo37HTlac-QmHl85C7loKqPkx5Ozg6V4sqAs6T2F-nfNhvbG3UUuFZP7oM0OBYlgH42qhOr_1OAnJUM2TPQw4lqhx8OQWts2EBi87Lkv9rLd7NgHYG-FEMkrc1ehe1Ux2Rr1hTytgz8IMK91uJ2EZqcUMP-xzc-QvFHSNKx7RyfWfT3AX8_juCWUsJ9ZQf7406232o7mnrqR0u9r7k8j7pbD6P8XqWPgX5TL0r_s-Lhaafqoeaz5IADJsNRDWE_KXNX_lrRnZRlpXyIMwF_K6u67tPGFh61OiSiO1mjGStZEeEaRebfdNJVeu8vsVBvpnS6xR6VFNcPjfjMoPk7Ob14KQ5dbBY0TXLvh4BOmRlSp9kVWRcINdX5RUszbdVUEIfmEur72kLUlUMw4qLRyDvXMpofKjYULSTj3qC1LavZWEeFn-b33xETk5GVniTQB5eRMJSGqx7gxAahf8zSubtAdfeYbg7Hl6HW3cvCpNHj2bJSCXE6gcw10ixPeNpEqoR15NhlbFFkYBu4VxLM3nD9SbNGd8cx0sl1d9dMGxFQ-v9KBRBssXYThAJTEsfNInvobM9i5U7t4VxuXgRe4cOQq5ZlsG_4uW1MSkypvalt8eeZZ9lG2IZsN-WQhEQsu9_cTRNq3iE69KZcQjyvcgd8Q==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c16000010748fcb_0%7C0a220b774c1a0000629e77ea_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EwKK9bjvnmuX6KYtPYDfJmDPY-PpSGD8dpJZc4MK1gj4j1dx59HuLM-MUcYJ8c-jlgI46RWQftIO4koAX7hV7N-iescCeL3UP_c3qcBtm7lOoULF5R0BU5-ZLSHrsWjqo37HTlac-QmHl85C7loKqPkx5Ozg6V4sqAs6T2F-nfNhvbG3UUuFZP7oM0OBYlgH42qhOr_1OAnJUM2TPQw4lqhx8OQWts2EBi87Lkv9rLd7NgHYG-FEMkrc1ehe1Ux2Rr1hTytgz8IMK91uJ2EZqcUMP-xzc-QvFHSNKx7RyfWfT3AX8_juCWUsJ9ZQf7406232o7mnrqR0u9r7k8j7pbD6P8XqWPgX5TL0r_s-Lhaafqoeaz5IADJsNRDWE_KXNX_lrRnZRlpXyIMwF_K6u67tPGFh61OiSiO1mjGStZEeEaRebfdNJVeu8vsVBvpnS6xR6VFNcPjfjMoPk7Ob14KQ5dbBY0TXLvh4BOmRlSp9kVWRcINdX5RUszbdVUEIfmEur72kLUlUMw4qLRyDvXMpofKjYULSTj3qC1LavZWEeFn-b33xETk5GVniTQB5eRMJSGqx7gxAahf8zSubtAdfeYbg7Hl6HW3cvCpNHj2bJSCXE6gcw10ixPeNpEqoR15NhlbFFkYBu4VxLM3nD9SbNGd8cx0sl1d9dMGxFQ-v9KBRBssXYThAJTEsfNInvobM9i5U7t4VxuXgRe4cOQq5ZlsG_4uW1MSkypvalt8eeZZ9lG2IZsN-WQhEQsu9_cTRNq3iE69KZcQjyvcgd8Q==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-01T19:45:00.000Z", "utc_arrival": "2023-05-01T17:45:00.000Z", "local_departure": "2023-05-01T16:15:00.000Z", "utc_departure": "2023-05-01T14:15:00.000Z"}, {"id": "0b770a224c210000eec7d4dd_0|0a220b774c250000060d8840_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 655.255769, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 192247.1296, "conversion": {"EUR": 503.256149, "HUF": 192247.1296}, "fare": {"adults": 96123.56, "children": 96123.56, "infants": 96123.56}, "bags_price": {"1": 68.992, "2": 137.984}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 4}, "airlines": ["FR"], "route": [{"id": "0b770a224c210000eec7d4dd_0", "combination_id": "0b770a224c210000eec7d4dd", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-12T21:45:00.000Z", "utc_arrival": "2023-05-12T19:45:00.000Z", "local_departure": "2023-05-12T18:25:00.000Z", "utc_departure": "2023-05-12T16:25:00.000Z"}, {"id": "0a220b774c250000060d8840_0", "combination_id": "0a220b774c250000060d8840", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-16T14:05:00.000Z", "utc_arrival": "2023-05-16T12:05:00.000Z", "local_departure": "2023-05-16T10:55:00.000Z", "utc_departure": "2023-05-16T08:55:00.000Z"}], "booking_token": "Em3ePZHr5njPoJ2O29uHJ8NUVo6Om3Vlrm4ieldN4-yKzbePT-YdEkmOZ4Qbd5QJ6yKWmVr7lFqkd6FmyPE7-AeyfwfTb3P6T9iLZOxuwjKCC7VDoXRRgAGFBbZX1ZsDm9Rz2kFx9Hrc4XlHvN8z70g9rQOoLyEFW4HsEejWdPSyyCB01BiXqYYz-zsJ-3DcomqLIe_UWcYkuOahNmAmp8QoNZaplnfeulpljOVl_ys6Oac9Y060D6QK-oUIwXOFXfylsaio0mH1M2QZRAVc0vReMddolqPBTeZmvVci0kuAfzvJypeElUNrJsXd5-ONPbHNObcchcaWcpyViMRHuznw5_iPm2Y0WC9dhQ_v0ufUXyZ8ixmO9ePLYziii7-WCVYkiS19UTXrCDVGdg9KH3k6roZc7F3lyXyHFYfX1KfOoCk4wEztKqte7n1nRW3Kor7AKffSrut_YSWOo1V9ygHAaAhn6KhpH02Blmx6A0eWQMOhYPQUkmz71bCtmrm-ZfeK-2F-vAEslxjF099t-0iiIjNZo9632OZkghI0vNGFG1Qj63dd58Dw3sNoQuFFDE7IbF5v_azaPJEG9WHAxLCi6SgHYOd6JRp-mwd0Ysk7UcMeWctWgXMPYW5YF07FMiouIvohT33kGN5zDeV3nT9mWlhMqzAxWNHWFuqdkhenqZUQ10ywBsjea6vvt_P9XxoLUcRn9n5GB54jCm6t_CRZVa1RTc_7030XvgAilMMxonK2ANihH3oS0yPxQuQiIjxNu-9ME-bcF_C3O80B6dg==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c210000eec7d4dd_0%7C0a220b774c250000060d8840_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=Em3ePZHr5njPoJ2O29uHJ8NUVo6Om3Vlrm4ieldN4-yKzbePT-YdEkmOZ4Qbd5QJ6yKWmVr7lFqkd6FmyPE7-AeyfwfTb3P6T9iLZOxuwjKCC7VDoXRRgAGFBbZX1ZsDm9Rz2kFx9Hrc4XlHvN8z70g9rQOoLyEFW4HsEejWdPSyyCB01BiXqYYz-zsJ-3DcomqLIe_UWcYkuOahNmAmp8QoNZaplnfeulpljOVl_ys6Oac9Y060D6QK-oUIwXOFXfylsaio0mH1M2QZRAVc0vReMddolqPBTeZmvVci0kuAfzvJypeElUNrJsXd5-ONPbHNObcchcaWcpyViMRHuznw5_iPm2Y0WC9dhQ_v0ufUXyZ8ixmO9ePLYziii7-WCVYkiS19UTXrCDVGdg9KH3k6roZc7F3lyXyHFYfX1KfOoCk4wEztKqte7n1nRW3Kor7AKffSrut_YSWOo1V9ygHAaAhn6KhpH02Blmx6A0eWQMOhYPQUkmz71bCtmrm-ZfeK-2F-vAEslxjF099t-0iiIjNZo9632OZkghI0vNGFG1Qj63dd58Dw3sNoQuFFDE7IbF5v_azaPJEG9WHAxLCi6SgHYOd6JRp-mwd0Ysk7UcMeWctWgXMPYW5YF07FMiouIvohT33kGN5zDeV3nT9mWlhMqzAxWNHWFuqdkhenqZUQ10ywBsjea6vvt_P9XxoLUcRn9n5GB54jCm6t_CRZVa1RTc_7030XvgAilMMxonK2ANihH3oS0yPxQuQiIjxNu-9ME-bcF_C3O80B6dg==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-12T21:45:00.000Z", "utc_arrival": "2023-05-12T19:45:00.000Z", "local_departure": "2023-05-12T18:25:00.000Z", "utc_departure": "2023-05-12T16:25:00.000Z"}, {"id": "0b770a224c330000e6ceb6e5_0|0a220b774c360000ea6a6a00_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 663.034567, "distance": 1975.87, "duration": {"departure": 12000, "return": 12900, "total": 24900}, "price": 192671.9774, "conversion": {"EUR": 504.368297, "HUF": 192671.9774}, "fare": {"adults": 96335.99, "children": 101265.61, "infants": 101265.61}, "bags_price": {"1": 89.082, "2": 178.164}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 2}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224c330000e6ceb6e5_0", "combination_id": "0b770a224c330000e6ceb6e5", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-30T10:15:00.000Z", "utc_arrival": "2023-05-30T08:15:00.000Z", "local_departure": "2023-05-30T06:55:00.000Z", "utc_departure": "2023-05-30T04:55:00.000Z"}, {"id": "0a220b774c360000ea6a6a00_0", "combination_id": "0a220b774c360000ea6a6a00", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "KREG", "fare_category": "M", "fare_classes": "K", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-03T00:05:00.000Z", "utc_arrival": "2023-06-02T22:05:00.000Z", "local_departure": "2023-06-02T20:30:00.000Z", "utc_departure": "2023-06-02T18:30:00.000Z"}], "booking_token": "EZsNW9D3aci-ygm6j4A6NOMjIk6yNJ9T7d4immWIQZ6hEHPux14pL1LUUSqS-Cd_8IccWH_wDVSPPdzsjYenrSF1WENR-C7dLnFURaRQW2DEBBmm93kQ7ahx_UpNFCvb5XQgDhF0V5dIJoCyMA7k79QeakzzetoVYEupnC6mx4AB6pzGVyTMh11QYqjijzS1TVMC9FNwpFN69TfYOnEFZd7opztILDjPIpTLl6GYhU_bjUPxy0Dlyt6i8t5mIB7YfXa4y3bFDcVJzuAZfR1x_B9Rx7LU0K9kC7a_DgjhgPdvas4TvoeVOdX2C55dikVE-zunRc6yDrntlNSojQMMak0PTT8Idef6IwwPXmfCEsTSAXZvniRHfTv75YhI_sz5XeN1yjAjYQc0_Nhf_7DA7C8mz1mN8AE9VHee4JN7o9nOrKNzRH3qQSJUCyzY1PVL9x0cmMnXvrrEE006ZYy2MgtjjHx4cF6x1Ge3cNtBnDMFAU7i_W8Uh-d4AMspAsPiYsI_lpmE170lOKVLFSmUDwr_t0ugsFwG9joNPBUivpem6fIHk6FOiMd3a26WJbAb7Z9elX2kfggO63d_hm1EPJ78uFlxB4pr16JsIL3TI2gk4pFqBSDdk_wTR_7joCGytfycJcmdXY3-O64WIukJY6F_psFVmBKI0dlfLwDjFALwfbkhnDrEs6vX9ayRxQgMDXUXZ-OxSTfPrB2AFMDUQqpDYlSS_M1TFjnTbBNBzhcycFQlSB7rjbhhTgvs3ZyY96cTKoLxfAhzGpetdrk1Zt1qxE06gdeDA3CWA7JlvWsE=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c330000e6ceb6e5_0%7C0a220b774c360000ea6a6a00_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EZsNW9D3aci-ygm6j4A6NOMjIk6yNJ9T7d4immWIQZ6hEHPux14pL1LUUSqS-Cd_8IccWH_wDVSPPdzsjYenrSF1WENR-C7dLnFURaRQW2DEBBmm93kQ7ahx_UpNFCvb5XQgDhF0V5dIJoCyMA7k79QeakzzetoVYEupnC6mx4AB6pzGVyTMh11QYqjijzS1TVMC9FNwpFN69TfYOnEFZd7opztILDjPIpTLl6GYhU_bjUPxy0Dlyt6i8t5mIB7YfXa4y3bFDcVJzuAZfR1x_B9Rx7LU0K9kC7a_DgjhgPdvas4TvoeVOdX2C55dikVE-zunRc6yDrntlNSojQMMak0PTT8Idef6IwwPXmfCEsTSAXZvniRHfTv75YhI_sz5XeN1yjAjYQc0_Nhf_7DA7C8mz1mN8AE9VHee4JN7o9nOrKNzRH3qQSJUCyzY1PVL9x0cmMnXvrrEE006ZYy2MgtjjHx4cF6x1Ge3cNtBnDMFAU7i_W8Uh-d4AMspAsPiYsI_lpmE170lOKVLFSmUDwr_t0ugsFwG9joNPBUivpem6fIHk6FOiMd3a26WJbAb7Z9elX2kfggO63d_hm1EPJ78uFlxB4pr16JsIL3TI2gk4pFqBSDdk_wTR_7joCGytfycJcmdXY3-O64WIukJY6F_psFVmBKI0dlfLwDjFALwfbkhnDrEs6vX9ayRxQgMDXUXZ-OxSTfPrB2AFMDUQqpDYlSS_M1TFjnTbBNBzhcycFQlSB7rjbhhTgvs3ZyY96cTKoLxfAhzGpetdrk1Zt1qxE06gdeDA3CWA7JlvWsE=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-30T10:15:00.000Z", "utc_arrival": "2023-05-30T08:15:00.000Z", "local_departure": "2023-05-30T06:55:00.000Z", "utc_departure": "2023-05-30T04:55:00.000Z"}, {"id": "0b770a224c25000076927589_0|0a220b774c290000987d29f5_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 657.727934, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 193191.5128, "conversion": {"EUR": 505.728314, "HUF": 193191.5128}, "fare": {"adults": 96595.76, "children": 96595.76, "infants": 96595.76}, "bags_price": {"1": 68.306, "2": 137.102}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 6}, "airlines": ["FR"], "route": [{"id": "0b770a224c25000076927589_0", "combination_id": "0b770a224c25000076927589", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-16T10:15:00.000Z", "utc_arrival": "2023-05-16T08:15:00.000Z", "local_departure": "2023-05-16T06:55:00.000Z", "utc_departure": "2023-05-16T04:55:00.000Z"}, {"id": "0a220b774c290000987d29f5_0", "combination_id": "0a220b774c290000987d29f5", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-20T09:40:00.000Z", "utc_arrival": "2023-05-20T07:40:00.000Z", "local_departure": "2023-05-20T06:30:00.000Z", "utc_departure": "2023-05-20T04:30:00.000Z"}], "booking_token": "E6JzkznADWIbEyTo-mFJScZDDDGlj2Bpzd7r8v4jrR6dowQQyNKzbVQllnrFaOa1Wjmg4kn2A0MNdV1OBmW_Dt3UNsxFrblbArNsTwiLaIkGPDFtV1cWreN13Ee1ua1UFWiOzgyRDnw1qqFiFBu4bdOjKrbmN88d6RuN-RXTxeYWcVFvuv65gyhhduS-siZ_J6m5hYNgL8lJtku444nr5cP3z-O-fXImw5moeHukx5GsJJdiNleysxGk9Q8rbNQcdkf_ZFwwpjZ2Lp0fn8Ie0VS0HZmwa7nnv9Yxi-sqRDG6E-UI2wpVAqqbYcjk0a5JXbXv36PB7HyFpN8UXc_hq-g3zuuPWrEux-lKYYs8GpxO_hGTTEopBqGWMGR7fljW61BzO4fm00JET6e32QblJS-fGWYT87SQ_u897QAh9hthaj1ZrsDePLcN_J67U0kKKkuQ94_3VzDNsCoI8Ajk7a5TmyGNG2cPj6JPycFCmgOFuy8qBsTFmPC36Np8W8AvMrLrxihGdkiCzZGgN_yxYS78GGe3DfUh7Ot0KrX1DaCpJynZVJhq0IKkXHyhTCVt-A5qKqcgk34hLFraBrrR7OI8QeJAwRqKvhGlfs975TioJVdDZdCIpCtb4Qx9PYIqBObBccCqmjQm72nZ8NYy2yl5Rspsk_UIQuEwYHv4EP1qEn1i_lZviHiP_PryLvs_nGP4FIcimdPFAkHcPmt_8Sg==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c25000076927589_0%7C0a220b774c290000987d29f5_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=E6JzkznADWIbEyTo-mFJScZDDDGlj2Bpzd7r8v4jrR6dowQQyNKzbVQllnrFaOa1Wjmg4kn2A0MNdV1OBmW_Dt3UNsxFrblbArNsTwiLaIkGPDFtV1cWreN13Ee1ua1UFWiOzgyRDnw1qqFiFBu4bdOjKrbmN88d6RuN-RXTxeYWcVFvuv65gyhhduS-siZ_J6m5hYNgL8lJtku444nr5cP3z-O-fXImw5moeHukx5GsJJdiNleysxGk9Q8rbNQcdkf_ZFwwpjZ2Lp0fn8Ie0VS0HZmwa7nnv9Yxi-sqRDG6E-UI2wpVAqqbYcjk0a5JXbXv36PB7HyFpN8UXc_hq-g3zuuPWrEux-lKYYs8GpxO_hGTTEopBqGWMGR7fljW61BzO4fm00JET6e32QblJS-fGWYT87SQ_u897QAh9hthaj1ZrsDePLcN_J67U0kKKkuQ94_3VzDNsCoI8Ajk7a5TmyGNG2cPj6JPycFCmgOFuy8qBsTFmPC36Np8W8AvMrLrxihGdkiCzZGgN_yxYS78GGe3DfUh7Ot0KrX1DaCpJynZVJhq0IKkXHyhTCVt-A5qKqcgk34hLFraBrrR7OI8QeJAwRqKvhGlfs975TioJVdDZdCIpCtb4Qx9PYIqBObBccCqmjQm72nZ8NYy2yl5Rspsk_UIQuEwYHv4EP1qEn1i_lZviHiP_PryLvs_nGP4FIcimdPFAkHcPmt_8Sg==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-16T10:15:00.000Z", "utc_arrival": "2023-05-16T08:15:00.000Z", "local_departure": "2023-05-16T06:55:00.000Z", "utc_departure": "2023-05-16T04:55:00.000Z"}, {"id": "0b770a224bfb0000cba453bb_0|0a220b774bff00008a5b783a_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 659.089409, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 193711.6051, "conversion": {"EUR": 507.089789, "HUF": 193711.6051}, "fare": {"adults": 96855.8, "children": 99199.09, "infants": 99199.09}, "bags_price": {"1": 122.528, "2": 245.07}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 4}, "airlines": ["FR"], "route": [{"id": "0b770a224bfb0000cba453bb_0", "combination_id": "0b770a224bfb0000cba453bb", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-04T10:15:00.000Z", "utc_arrival": "2023-04-04T08:15:00.000Z", "local_departure": "2023-04-04T06:55:00.000Z", "utc_departure": "2023-04-04T04:55:00.000Z"}, {"id": "0a220b774bff00008a5b783a_0", "combination_id": "0a220b774bff00008a5b783a", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-08T09:40:00.000Z", "utc_arrival": "2023-04-08T07:40:00.000Z", "local_departure": "2023-04-08T06:30:00.000Z", "utc_departure": "2023-04-08T04:30:00.000Z"}], "booking_token": "ECWm-nOsHOttDSzQOXmPyfzbBzaHCWi5tUT93Vtxv8ga7boU43te8RNFyHKto4chjZxYIROoAjvccT3_ROk3JS-UhmMlsB_oY20lpQ3rQgCR1obr8ljRuJGwOJnZ_XebEzO6WWzhy6eGt2XV9mRcttuJ7p4ISIrc76G8lDwzKPmnQlzOPCQWtphsqa-XfhkyiKcg1tufqtMYvkznKxPO-RKE9E4OuOXkAlsRVNw9qPV3Cl6rj2Dr2RShhDf6v76tp2jVRViddKgD9SqmJoYPZju4biHo6ptOKl6zLAYz59__nPlwF8Q5oH8iHMu3YkJ6SWFG7Pb7k5LbFxs0yDhTaw36Jr0ucym_rvHUJnGMUgSEGPYvm2Xpx9k5Nb8ea61yupvLvQoxH_bPPzRnm6z54lmTo45qqFtEGIHgBU8L5Q585jlNeH92Dqv5Sk5EqRdFY2ciJ9IG9MODh_loiGQjC5AGrh7m60RJKrlqfGbc70qvzxbDot3kNb3Hn1JJ_UM-64VKV2Zyxebsepkb75_NsCeiJpvaoQe-_-hSIRcUiXB8eDddn3SBC2V86a4Aynm5LfFUrUqrqXB0yUDqjXUYnAFUJJj5CeCTpcM-EqaO5pSGiya_zd3_DIV8F-0nGMjIusRf9Ig7KT6zaplQleMG8T9SlWcpzpyM2--jRfeK9Y_LVuLkdtzKqJcr_YKILvfeiznH_LEXiaMA2P9qvbg53nfoEJ_MsuqNJi9DwIQCr4cUM2_BlJIUh2CZPNc41mwYBdK9YXb_lfxejS5xlsIbb-Q==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224bfb0000cba453bb_0%7C0a220b774bff00008a5b783a_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=ECWm-nOsHOttDSzQOXmPyfzbBzaHCWi5tUT93Vtxv8ga7boU43te8RNFyHKto4chjZxYIROoAjvccT3_ROk3JS-UhmMlsB_oY20lpQ3rQgCR1obr8ljRuJGwOJnZ_XebEzO6WWzhy6eGt2XV9mRcttuJ7p4ISIrc76G8lDwzKPmnQlzOPCQWtphsqa-XfhkyiKcg1tufqtMYvkznKxPO-RKE9E4OuOXkAlsRVNw9qPV3Cl6rj2Dr2RShhDf6v76tp2jVRViddKgD9SqmJoYPZju4biHo6ptOKl6zLAYz59__nPlwF8Q5oH8iHMu3YkJ6SWFG7Pb7k5LbFxs0yDhTaw36Jr0ucym_rvHUJnGMUgSEGPYvm2Xpx9k5Nb8ea61yupvLvQoxH_bPPzRnm6z54lmTo45qqFtEGIHgBU8L5Q585jlNeH92Dqv5Sk5EqRdFY2ciJ9IG9MODh_loiGQjC5AGrh7m60RJKrlqfGbc70qvzxbDot3kNb3Hn1JJ_UM-64VKV2Zyxebsepkb75_NsCeiJpvaoQe-_-hSIRcUiXB8eDddn3SBC2V86a4Aynm5LfFUrUqrqXB0yUDqjXUYnAFUJJj5CeCTpcM-EqaO5pSGiya_zd3_DIV8F-0nGMjIusRf9Ig7KT6zaplQleMG8T9SlWcpzpyM2--jRfeK9Y_LVuLkdtzKqJcr_YKILvfeiznH_LEXiaMA2P9qvbg53nfoEJ_MsuqNJi9DwIQCr4cUM2_BlJIUh2CZPNc41mwYBdK9YXb_lfxejS5xlsIbb-Q==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-04-04T10:15:00.000Z", "utc_arrival": "2023-04-04T08:15:00.000Z", "local_departure": "2023-04-04T06:55:00.000Z", "utc_departure": "2023-04-04T04:55:00.000Z"}, {"id": "0b770a224c210000eec7d4dd_0|0a220b774c2400009a975815_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 661.7766, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 194738.1296, "conversion": {"EUR": 509.77698, "HUF": 194738.1296}, "fare": {"adults": 97369.06, "children": 97369.06, "infants": 97369.06}, "bags_price": {"1": 69.678, "2": 139.356}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 4}, "airlines": ["FR"], "route": [{"id": "0b770a224c210000eec7d4dd_0", "combination_id": "0b770a224c210000eec7d4dd", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-12T21:45:00.000Z", "utc_arrival": "2023-05-12T19:45:00.000Z", "local_departure": "2023-05-12T18:25:00.000Z", "utc_departure": "2023-05-12T16:25:00.000Z"}, {"id": "0a220b774c2400009a975815_0", "combination_id": "0a220b774c2400009a975815", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-15T10:15:00.000Z", "utc_arrival": "2023-05-15T08:15:00.000Z", "local_departure": "2023-05-15T07:05:00.000Z", "utc_departure": "2023-05-15T05:05:00.000Z"}], "booking_token": "ELGWtC3OD473aKgxUvvMJG4K3Mz0aqNzdnzrjiv5MrnSb0-71_22iTVlkLY1coRU0a0NEMU2gSBdY6dtOOBQ6nj4PqSjVsbE75MWW45DsB7fCy7LT9G3ircwgveWq1cRi0sPAN3tYkC31UXZRSzM0Vr8t6je-llrcowbYIH3BXm6m1s0E0UujUy8TIMu8v_IHI_EL8RputuAm6N_41vtBv1ZxmkyXlRN96kUkq7FWX1hShRnY1Ir9nRqxXFSq63thXgoT_Cp_qxTQTOKqI1GRK50T1635ODUh8uJd-h1HQdtITGM2jl2VKJNCsPdp2hEUkpcciD5Qc8yzP6MErcrCWOR2W8A2Eqq5Acx8ZN2QUDrDv9Dsxz-DT8WpRmbxiiZWhY91TdzQQMMhB6Y-90ZyIIvt1cHZOLHBZltd9nGWvtQru61arbZrxrwZkodunHT6OV1tQxC1cux4vOnGbToWQMdfwTHWnF3YD5_0FTrH5hK7eArNIGKWRHGW4SlLj3wSYhG4BI9fUo0-yu_XFjSnV9TZwH3sZ_hu3CLHqP9-7ouYZea5jZ4FhDaHbu9br0406l4R0IZJMt_o0rVdTZeR35VodJw04vplOro2hssUJ2ioi3Zq0GKgKCW5S8bEJolUrNxkhrpjbiBQ2PRiv9t3hMSCg4Jk0-GT0s-CSqacap5c9iZgYYh177BwFVYPF4J7H0shgBJNeLwbsh9Dhd93NrvgkcSdWaU6D7ENpKmn6Kv-trnv0C0_vzJ9q7-19HCOyXXcvGTp5wE2YnRcWUbS8Td1rYJ2Ea-vdUtbNbqKNG4=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c210000eec7d4dd_0%7C0a220b774c2400009a975815_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=ELGWtC3OD473aKgxUvvMJG4K3Mz0aqNzdnzrjiv5MrnSb0-71_22iTVlkLY1coRU0a0NEMU2gSBdY6dtOOBQ6nj4PqSjVsbE75MWW45DsB7fCy7LT9G3ircwgveWq1cRi0sPAN3tYkC31UXZRSzM0Vr8t6je-llrcowbYIH3BXm6m1s0E0UujUy8TIMu8v_IHI_EL8RputuAm6N_41vtBv1ZxmkyXlRN96kUkq7FWX1hShRnY1Ir9nRqxXFSq63thXgoT_Cp_qxTQTOKqI1GRK50T1635ODUh8uJd-h1HQdtITGM2jl2VKJNCsPdp2hEUkpcciD5Qc8yzP6MErcrCWOR2W8A2Eqq5Acx8ZN2QUDrDv9Dsxz-DT8WpRmbxiiZWhY91TdzQQMMhB6Y-90ZyIIvt1cHZOLHBZltd9nGWvtQru61arbZrxrwZkodunHT6OV1tQxC1cux4vOnGbToWQMdfwTHWnF3YD5_0FTrH5hK7eArNIGKWRHGW4SlLj3wSYhG4BI9fUo0-yu_XFjSnV9TZwH3sZ_hu3CLHqP9-7ouYZea5jZ4FhDaHbu9br0406l4R0IZJMt_o0rVdTZeR35VodJw04vplOro2hssUJ2ioi3Zq0GKgKCW5S8bEJolUrNxkhrpjbiBQ2PRiv9t3hMSCg4Jk0-GT0s-CSqacap5c9iZgYYh177BwFVYPF4J7H0shgBJNeLwbsh9Dhd93NrvgkcSdWaU6D7ENpKmn6Kv-trnv0C0_vzJ9q7-19HCOyXXcvGTp5wE2YnRcWUbS8Td1rYJ2Ea-vdUtbNbqKNG4=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-12T21:45:00.000Z", "utc_arrival": "2023-05-12T19:45:00.000Z", "local_departure": "2023-05-12T18:25:00.000Z", "utc_departure": "2023-05-12T16:25:00.000Z"}, {"id": "0b770a224c4b00004d10476b_0|0a220b774c4e000024b82646_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 664.671754, "distance": 1975.87, "duration": {"departure": 12600, "return": 11400, "total": 24000}, "price": 194825.4158, "conversion": {"EUR": 510.005474, "HUF": 194825.4158}, "fare": {"adults": 97412.71, "children": 97412.71, "infants": 97412.71}, "bags_price": {"1": 103.11, "2": 206.206}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 3}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224c4b00004d10476b_0", "combination_id": "0b770a224c4b00004d10476b", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IJREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-23T19:45:00.000Z", "utc_arrival": "2023-06-23T17:45:00.000Z", "local_departure": "2023-06-23T16:15:00.000Z", "utc_departure": "2023-06-23T14:15:00.000Z"}, {"id": "0a220b774c4e000024b82646_0", "combination_id": "0a220b774c4e000024b82646", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-26T10:15:00.000Z", "utc_arrival": "2023-06-26T08:15:00.000Z", "local_departure": "2023-06-26T07:05:00.000Z", "utc_departure": "2023-06-26T05:05:00.000Z"}], "booking_token": "EESgOlw5ZnwkoVjjTcmkoPJjcRsCsPve0WJHOseaFMHPohkhX7tkIvspo3RRkFPaxE9ZCFS1lO8Ague-wjvv9K0lRv-JS0YqyMa5B41d--FDfxS3ImXLho3-cTQNmnwghDGHLjbdl0m6Y4DHKUtHj7RcdtGKJGBT3z8FcOyH1kPr7YC3S0zxhe5UH8AC14lroT-MZjgqQcd3Bd1r8C0m70AXbZI14m2RhVdSXu0GRfcgTXHfVOk0s28D3tRMbCezozc3vlEwCkysFoIm67QP-Wo8uGSCSNEJaO4IIUiJ4FRbwbgAzI2l3sJYT0gbsnXrsk0arJ6zEQ2rOn0sIZB5WjzCMP4SwLySGGhilEe9tMNFMT4BlP6y000Eo8VM27YPlUBSwk0p5M1FHHzA-2B0tLCn80jvKlOqQtQ7XStV6VgksebInlbvnNcIkoBbjEiAIeCVYq9hO9R5xljTQBeLrhc7JiJY1WH3QrX_nLzMKkGRkCNclz4efyVS5Bo4ANSDzUSve0h_qmHbcbQJ5JQa9j9jIl8NKZ-1FXrooZZ8pY2gM8EUX8NA1IJqXnw0YGunSppQYp3iTXczXrIiy0z9MJG-1xMFEHT5GbyAjunoM945PP459OpKV6q--Po9_W-Dfi84Ai2RkGINWLKlp_16ZRwS-jmxk9d7Znv4BmWNB92BwY1zXS8U4JZ-CHBIq51kRn_67DDvk7bDqVYd6mUXShSoxsix0zfPtHM2WFXw30v6RafO0DJxOp6TcEz4ET7gkgfEsrig8ZvQW2dIEFiyqtQ==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c4b00004d10476b_0%7C0a220b774c4e000024b82646_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EESgOlw5ZnwkoVjjTcmkoPJjcRsCsPve0WJHOseaFMHPohkhX7tkIvspo3RRkFPaxE9ZCFS1lO8Ague-wjvv9K0lRv-JS0YqyMa5B41d--FDfxS3ImXLho3-cTQNmnwghDGHLjbdl0m6Y4DHKUtHj7RcdtGKJGBT3z8FcOyH1kPr7YC3S0zxhe5UH8AC14lroT-MZjgqQcd3Bd1r8C0m70AXbZI14m2RhVdSXu0GRfcgTXHfVOk0s28D3tRMbCezozc3vlEwCkysFoIm67QP-Wo8uGSCSNEJaO4IIUiJ4FRbwbgAzI2l3sJYT0gbsnXrsk0arJ6zEQ2rOn0sIZB5WjzCMP4SwLySGGhilEe9tMNFMT4BlP6y000Eo8VM27YPlUBSwk0p5M1FHHzA-2B0tLCn80jvKlOqQtQ7XStV6VgksebInlbvnNcIkoBbjEiAIeCVYq9hO9R5xljTQBeLrhc7JiJY1WH3QrX_nLzMKkGRkCNclz4efyVS5Bo4ANSDzUSve0h_qmHbcbQJ5JQa9j9jIl8NKZ-1FXrooZZ8pY2gM8EUX8NA1IJqXnw0YGunSppQYp3iTXczXrIiy0z9MJG-1xMFEHT5GbyAjunoM945PP459OpKV6q--Po9_W-Dfi84Ai2RkGINWLKlp_16ZRwS-jmxk9d7Znv4BmWNB92BwY1zXS8U4JZ-CHBIq51kRn_67DDvk7bDqVYd6mUXShSoxsix0zfPtHM2WFXw30v6RafO0DJxOp6TcEz4ET7gkgfEsrig8ZvQW2dIEFiyqtQ==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-23T19:45:00.000Z", "utc_arrival": "2023-06-23T17:45:00.000Z", "local_departure": "2023-06-23T16:15:00.000Z", "utc_departure": "2023-06-23T14:15:00.000Z"}, {"id": "0b770a224c32000091ac2e03_0|0a220b774c360000ea6a6a00_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 669.59953, "distance": 1975.87, "duration": {"departure": 12000, "return": 12900, "total": 24900}, "price": 195179.8361, "conversion": {"EUR": 510.93326, "HUF": 195179.8361}, "fare": {"adults": 97589.92, "children": 97589.92, "infants": 97589.92}, "bags_price": {"1": 88.396, "2": 176.792}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 2}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224c32000091ac2e03_0", "combination_id": "0b770a224c32000091ac2e03", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-29T14:00:00.000Z", "utc_arrival": "2023-05-29T12:00:00.000Z", "local_departure": "2023-05-29T10:40:00.000Z", "utc_departure": "2023-05-29T08:40:00.000Z"}, {"id": "0a220b774c360000ea6a6a00_0", "combination_id": "0a220b774c360000ea6a6a00", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "KREG", "fare_category": "M", "fare_classes": "K", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-03T00:05:00.000Z", "utc_arrival": "2023-06-02T22:05:00.000Z", "local_departure": "2023-06-02T20:30:00.000Z", "utc_departure": "2023-06-02T18:30:00.000Z"}], "booking_token": "EpDdk_FAXQFse8o3nREWl34FpsYuVsNEzR2ARi9_5Ov_Ykp5ojnz219D__YKaXw_vMjlZT9-4vKsJxzdlr6svYXWRM0oWzooHfsaqIeeW_Msne9wYQzARnLrmVCQrO5RkYHQByYqx1ffAy9jZknf8WtG1wQzddn_4u7MiASRJnsLr8ZNXtZmB3A_PkdqxBgNFVS0nIET1MoPnV4CK3j4E1Fx2udjCNbEfu7XWngJPK2UQEpaDtoobh0PviuQ-e9Z0X8EG5Ij31RL5Wt2I43KGFN8gNlHvwVZyki4sen341yEX4W0SJ5LjttcvgUnPR7c7caR0CVULKBuJS9yg-UdoKz5TD-d1YUjtC6gNbGK4co9b5wE4ucThdHEA-BxYUG0ZojqWpg1fa_1Hz0XHU3tn81MvUE4geXezCG3Y9iqi614Sn4jUnW6iF9wi6prSWeEhut4klotBdOeTjA1JleWCkQUlRATvEaQMnjnGI0XxtfK7Taf5vNkyjHFtA7ltRvbm7xLQnWQV6Ykv3bhumPcjW5vSwGqyPtLsbDykzIQkH-yhAdpA1i4cQj0Z2B5yNNyEuUZ-CG3EvOEzZyYmdnkcvD4qb8EU8KqRJNJx2AtZEx9sMuaOOs1pCTsgwz0VTFoBK3TjhlXsVkGTWnJGBGqm-2sagbi3OLjTAjWVvWWCySb-k-5aVs4maiV6KDeL1MkT9PLPavKBAU4NE3ddj0lm4FQAO8kqXWUT_zj4cY4DbafAmHze8_rqA6OTe6he66TQQ1jdIaJODGegOCw5m5x8mA==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c32000091ac2e03_0%7C0a220b774c360000ea6a6a00_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EpDdk_FAXQFse8o3nREWl34FpsYuVsNEzR2ARi9_5Ov_Ykp5ojnz219D__YKaXw_vMjlZT9-4vKsJxzdlr6svYXWRM0oWzooHfsaqIeeW_Msne9wYQzARnLrmVCQrO5RkYHQByYqx1ffAy9jZknf8WtG1wQzddn_4u7MiASRJnsLr8ZNXtZmB3A_PkdqxBgNFVS0nIET1MoPnV4CK3j4E1Fx2udjCNbEfu7XWngJPK2UQEpaDtoobh0PviuQ-e9Z0X8EG5Ij31RL5Wt2I43KGFN8gNlHvwVZyki4sen341yEX4W0SJ5LjttcvgUnPR7c7caR0CVULKBuJS9yg-UdoKz5TD-d1YUjtC6gNbGK4co9b5wE4ucThdHEA-BxYUG0ZojqWpg1fa_1Hz0XHU3tn81MvUE4geXezCG3Y9iqi614Sn4jUnW6iF9wi6prSWeEhut4klotBdOeTjA1JleWCkQUlRATvEaQMnjnGI0XxtfK7Taf5vNkyjHFtA7ltRvbm7xLQnWQV6Ykv3bhumPcjW5vSwGqyPtLsbDykzIQkH-yhAdpA1i4cQj0Z2B5yNNyEuUZ-CG3EvOEzZyYmdnkcvD4qb8EU8KqRJNJx2AtZEx9sMuaOOs1pCTsgwz0VTFoBK3TjhlXsVkGTWnJGBGqm-2sagbi3OLjTAjWVvWWCySb-k-5aVs4maiV6KDeL1MkT9PLPavKBAU4NE3ddj0lm4FQAO8kqXWUT_zj4cY4DbafAmHze8_rqA6OTe6he66TQQ1jdIaJODGegOCw5m5x8mA==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-29T14:00:00.000Z", "utc_arrival": "2023-05-29T12:00:00.000Z", "local_departure": "2023-05-29T10:40:00.000Z", "utc_departure": "2023-05-29T08:40:00.000Z"}, {"id": "0b770a224bef0000e50ad4c9_0|0a220b774bf30000da5652ad_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 663.759988, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 195495.7967, "conversion": {"EUR": 511.760368, "HUF": 195495.7967}, "fare": {"adults": 97747.9, "children": 97747.9, "infants": 97747.9}, "bags_price": {"1": 87.486, "2": 174.958}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 2}, "airlines": ["FR"], "route": [{"id": "0b770a224bef0000e50ad4c9_0", "combination_id": "0b770a224bef0000e50ad4c9", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-03-23T13:40:00.000Z", "utc_arrival": "2023-03-23T12:40:00.000Z", "local_departure": "2023-03-23T10:20:00.000Z", "utc_departure": "2023-03-23T09:20:00.000Z"}, {"id": "0a220b774bf30000da5652ad_0", "combination_id": "0a220b774bf30000da5652ad", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-03-27T10:15:00.000Z", "utc_arrival": "2023-03-27T08:15:00.000Z", "local_departure": "2023-03-27T07:05:00.000Z", "utc_departure": "2023-03-27T05:05:00.000Z"}], "booking_token": "E_VxGoF0fnwBNLeUaQZxkY2pCo7km1OfnOphSiLU0jmxqGJU1qE_FKVFJu0IzaxcM7p4v2jY0_VFTUycJSm28WbZnCj0XzWra800k3r1mDifEOs5DZ8bz0PnlQGtUSQ2rf6K4pj-LIUjavtoaoW8T-GCympRpCT2xWKpugBtw3T9JIEq8ONh2X18FxxUfB0K149tbvKw9NWjupQfNzpprj114GWQscw2A_U_tffoTk0GFIVjKueJWsapSK-XR5tL9Js6IOm0M-iOWgQqVq-JMHmnSMkmn_UFxf2hWfB8icQ0PocUvbsxS29kS5GUyeTgwmWjt2COdRDjo3FYzbb9U3NWbVZLqLxo0jmv1mUHkOiZVw9ikqP50gcIaDBLPPXVA8hVxROU8AMYvRHFb4oZK-xXQwMn3Ys3lI1UekfBjRddMihVmnBvOO1RLgl0pYHdWcg_u_WxsaKbQfZ2vB1mrhtPE0K5WQAmRZNrb1wUdUq19R5IIp7YBt9-RRXzEaf_8FQEqMjvgirtjLVNB2hpqAGDuH_lVQ3C223RFs-VJ70EHLHpawyYJzT5cJuEAXelz4hw-EN35ayY4j9WDlBlSGLzyZvWNv1S-NgXUJqW2BeohHdKvxzNsHUF3fPV86OuAczNUDAtFfgdq_4GbaeebT2A5u2tq6ydMAnJe0EQdnETCNybJWMGFzCweT6tgQaCTesFrwDIy0VOiTRBAk67TQCBvuajRs9KaMeghR-rsRiorH_LkPpn5bOCSI_Oc8v1i3W4oyv0-Lcv644tX7lc5xw==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224bef0000e50ad4c9_0%7C0a220b774bf30000da5652ad_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=E_VxGoF0fnwBNLeUaQZxkY2pCo7km1OfnOphSiLU0jmxqGJU1qE_FKVFJu0IzaxcM7p4v2jY0_VFTUycJSm28WbZnCj0XzWra800k3r1mDifEOs5DZ8bz0PnlQGtUSQ2rf6K4pj-LIUjavtoaoW8T-GCympRpCT2xWKpugBtw3T9JIEq8ONh2X18FxxUfB0K149tbvKw9NWjupQfNzpprj114GWQscw2A_U_tffoTk0GFIVjKueJWsapSK-XR5tL9Js6IOm0M-iOWgQqVq-JMHmnSMkmn_UFxf2hWfB8icQ0PocUvbsxS29kS5GUyeTgwmWjt2COdRDjo3FYzbb9U3NWbVZLqLxo0jmv1mUHkOiZVw9ikqP50gcIaDBLPPXVA8hVxROU8AMYvRHFb4oZK-xXQwMn3Ys3lI1UekfBjRddMihVmnBvOO1RLgl0pYHdWcg_u_WxsaKbQfZ2vB1mrhtPE0K5WQAmRZNrb1wUdUq19R5IIp7YBt9-RRXzEaf_8FQEqMjvgirtjLVNB2hpqAGDuH_lVQ3C223RFs-VJ70EHLHpawyYJzT5cJuEAXelz4hw-EN35ayY4j9WDlBlSGLzyZvWNv1S-NgXUJqW2BeohHdKvxzNsHUF3fPV86OuAczNUDAtFfgdq_4GbaeebT2A5u2tq6ydMAnJe0EQdnETCNybJWMGFzCweT6tgQaCTesFrwDIy0VOiTRBAk67TQCBvuajRs9KaMeghR-rsRiorH_LkPpn5bOCSI_Oc8v1i3W4oyv0-Lcv644tX7lc5xw==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-03-23T13:40:00.000Z", "utc_arrival": "2023-03-23T12:40:00.000Z", "local_departure": "2023-03-23T10:20:00.000Z", "utc_departure": "2023-03-23T09:20:00.000Z"}, {"id": "0b770a224c4b0000ee8a8a37_0|0a220b774c4e000024b82646_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 662.865101, "distance": 1975.87, "duration": {"departure": 11700, "return": 11400, "total": 23100}, "price": 195663.2848, "conversion": {"EUR": 512.198811, "HUF": 195663.2848}, "fare": {"adults": 97831.64, "children": 97831.64, "infants": 97831.64}, "bags_price": {"1": 76.986, "2": 163.772}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 158, "hold_height": 52, "hold_length": 78, "hold_weight": 20, "hold_width": 28, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 3, "personal_item_width": 15}, "availability": {"seats": 3}, "airlines": ["FR", "IB"], "route": [{"id": "0b770a224c4b0000ee8a8a37_0", "combination_id": "0b770a224c4b0000ee8a8a37", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "IB", "flight_no": 3279, "operating_carrier": "IB", "operating_flight_no": "3279", "fare_basis": "QWNNAOB4", "fare_category": "M", "fare_classes": "Q", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-23T18:50:00.000Z", "utc_arrival": "2023-06-23T16:50:00.000Z", "local_departure": "2023-06-23T15:35:00.000Z", "utc_departure": "2023-06-23T13:35:00.000Z"}, {"id": "0a220b774c4e000024b82646_0", "combination_id": "0a220b774c4e000024b82646", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-26T10:15:00.000Z", "utc_arrival": "2023-06-26T08:15:00.000Z", "local_departure": "2023-06-26T07:05:00.000Z", "utc_departure": "2023-06-26T05:05:00.000Z"}], "booking_token": "EVtylLhaDzazVAXyOAplgrFuqEMqQJJk_Q8nrsNnyqEP9BBHISnvSam0abAlwEqjSN7OwcOKXC3d-julB4_hM-P349SJqV_Ura-coGNPmyPGgz77prRPFOGUa9FeIT-YgkUDM3YDADj473xCQMqALzYmI_klfjBxWaKbhrFUHxYP31fm8ArXapIWe67uUPWVC6dDaCEc82icCHoHVe3qQGxzQrMmBsDZFUxKQf0ZT10VxeGonyZaGOMGOHPVj4eDdacBrhzH8Llkw8zsSWOgY0mfWuqgV0T2S7FM1hKY38kyKusJ_BkvQfZF39J0YyW6JWpzauPXZDq5W3CZ9PhCUMBG3-bjhr_vJxc8hjfEIVglzPU8d47r6UrkdwR3TDzG5kwDHasQAwZuwVF17N5T8ggWid4_QO77xNweXXd7PvFDGq8PKAom2zZaHvTJjrN9-uJHTyoAGZBOpuBEL6TA7Kvef8btILA-X7Zcc4IEIUZ9iALe5ntB9VeK_SVKUzXzl5B3j8y47mCeS5y6AqWBAbBPzuPMNl98AnKdyoWd1kS2Xf1yMhlt8JST51MpJLVF8v7Yg46q4wFsy_mWRaqWyyDX601gjuktwp0sCGbmaaRTQFqDgA6nv7nrIAplIgpvy5_PwlH4winyWEQ87S6vwg1ikCKWi_JdnmfZ3OrKGU8lJuXDN16CdgUfxwV9UD6vokxVenZiE1a5k8ionYhlB0oO0G1r_F9Czc7JLSAxwSxpDob40NBYXrJSq74tICOL5FNcVp-3DeFexX1jtdv962U8x68eWVdFA22SVMPO_dXE=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c4b0000ee8a8a37_0%7C0a220b774c4e000024b82646_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EVtylLhaDzazVAXyOAplgrFuqEMqQJJk_Q8nrsNnyqEP9BBHISnvSam0abAlwEqjSN7OwcOKXC3d-julB4_hM-P349SJqV_Ura-coGNPmyPGgz77prRPFOGUa9FeIT-YgkUDM3YDADj473xCQMqALzYmI_klfjBxWaKbhrFUHxYP31fm8ArXapIWe67uUPWVC6dDaCEc82icCHoHVe3qQGxzQrMmBsDZFUxKQf0ZT10VxeGonyZaGOMGOHPVj4eDdacBrhzH8Llkw8zsSWOgY0mfWuqgV0T2S7FM1hKY38kyKusJ_BkvQfZF39J0YyW6JWpzauPXZDq5W3CZ9PhCUMBG3-bjhr_vJxc8hjfEIVglzPU8d47r6UrkdwR3TDzG5kwDHasQAwZuwVF17N5T8ggWid4_QO77xNweXXd7PvFDGq8PKAom2zZaHvTJjrN9-uJHTyoAGZBOpuBEL6TA7Kvef8btILA-X7Zcc4IEIUZ9iALe5ntB9VeK_SVKUzXzl5B3j8y47mCeS5y6AqWBAbBPzuPMNl98AnKdyoWd1kS2Xf1yMhlt8JST51MpJLVF8v7Yg46q4wFsy_mWRaqWyyDX601gjuktwp0sCGbmaaRTQFqDgA6nv7nrIAplIgpvy5_PwlH4winyWEQ87S6vwg1ikCKWi_JdnmfZ3OrKGU8lJuXDN16CdgUfxwV9UD6vokxVenZiE1a5k8ionYhlB0oO0G1r_F9Czc7JLSAxwSxpDob40NBYXrJSq74tICOL5FNcVp-3DeFexX1jtdv962U8x68eWVdFA22SVMPO_dXE=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-23T18:50:00.000Z", "utc_arrival": "2023-06-23T16:50:00.000Z", "local_departure": "2023-06-23T15:35:00.000Z", "utc_departure": "2023-06-23T13:35:00.000Z"}, {"id": "0b770a224c25000076927589_0|0a220b774c28000046de2a57_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 672.334056, "distance": 1975.87, "duration": {"departure": 12000, "return": 12900, "total": 24900}, "price": 196224.4429, "conversion": {"EUR": 513.667786, "HUF": 196224.4429}, "fare": {"adults": 98112.22, "children": 98112.22, "infants": 98112.22}, "bags_price": {"1": 75.796, "2": 152.096}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 4}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224c25000076927589_0", "combination_id": "0b770a224c25000076927589", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-16T10:15:00.000Z", "utc_arrival": "2023-05-16T08:15:00.000Z", "local_departure": "2023-05-16T06:55:00.000Z", "utc_departure": "2023-05-16T04:55:00.000Z"}, {"id": "0a220b774c28000046de2a57_0", "combination_id": "0a220b774c28000046de2a57", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "JKREG", "fare_category": "M", "fare_classes": "J", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-20T00:05:00.000Z", "utc_arrival": "2023-05-19T22:05:00.000Z", "local_departure": "2023-05-19T20:30:00.000Z", "utc_departure": "2023-05-19T18:30:00.000Z"}], "booking_token": "EHC8eXHiQ1aMTXq2bgWSFe9RiBpIKFkp0SiMbvV8BOyr-zvkgXlaB9NfrVHAaMWuYEnWrhsdTrF35TanCnibH8Uu5JHQ65X6HdCrfUXw5TnTml9wxJ_i7p2Hw_Gk5TnpjMp9iV7iSnJzyVUeDooY9B_3iOYhuEa-Sr-EAhvH8b_Wz7UeUcy8L94So9y-2M6zWtRqTHj6MX3vHebA3LZiWbHN2KpabMcy-IG9Ct_DAVj5JdN4Z8xwpnm7CKnboWbL99zaNFHmDg6xPsAiXHx7-apKob9i665oov2nnhrXkO20_-amzVWV6nz_NIOoVje78PWF3tYlPiTL2aclvmIjpITMmkK84TWYSQhO65cH4YYcbdbnMN8iizcduH5YV6m8WQMObvDCEVUMcONWpbIgpDaleOtfnyqwwzYtOyYHtrnyzTEWLnlPis5-EnWsCgzmNM2Jp9XuMVj3nxktas1d5V1GV2g6o304P01h8TyNpmiRR5VH6JGH-7Km5wwADnBQbgult6PAZ82qTVP_M33939cfnyknjaY1tmdapD9Oizm7OjR3Uchlif_tX1Xv4o2SzBkd_xTCxUCtBSmPvdp2Z_6-EDbjKr7FPAn2yLz7ct8rJESURFG9f5ddnj-XfV9oPqN8RaKgmQzmFUUChVDIPuXBAbzvDjpsZPzhokNWKLaT2v-59mXEDBI64jwBpEqfkDARpWmpQcbH9qhwN0PRXhaJ6sCFUMHrvOhH0BvEPlGKhwxOigEraNMRBOKyxEfY_8_JgwuQ5X3Y7T2NZ8szt8g==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c25000076927589_0%7C0a220b774c28000046de2a57_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EHC8eXHiQ1aMTXq2bgWSFe9RiBpIKFkp0SiMbvV8BOyr-zvkgXlaB9NfrVHAaMWuYEnWrhsdTrF35TanCnibH8Uu5JHQ65X6HdCrfUXw5TnTml9wxJ_i7p2Hw_Gk5TnpjMp9iV7iSnJzyVUeDooY9B_3iOYhuEa-Sr-EAhvH8b_Wz7UeUcy8L94So9y-2M6zWtRqTHj6MX3vHebA3LZiWbHN2KpabMcy-IG9Ct_DAVj5JdN4Z8xwpnm7CKnboWbL99zaNFHmDg6xPsAiXHx7-apKob9i665oov2nnhrXkO20_-amzVWV6nz_NIOoVje78PWF3tYlPiTL2aclvmIjpITMmkK84TWYSQhO65cH4YYcbdbnMN8iizcduH5YV6m8WQMObvDCEVUMcONWpbIgpDaleOtfnyqwwzYtOyYHtrnyzTEWLnlPis5-EnWsCgzmNM2Jp9XuMVj3nxktas1d5V1GV2g6o304P01h8TyNpmiRR5VH6JGH-7Km5wwADnBQbgult6PAZ82qTVP_M33939cfnyknjaY1tmdapD9Oizm7OjR3Uchlif_tX1Xv4o2SzBkd_xTCxUCtBSmPvdp2Z_6-EDbjKr7FPAn2yLz7ct8rJESURFG9f5ddnj-XfV9oPqN8RaKgmQzmFUUChVDIPuXBAbzvDjpsZPzhokNWKLaT2v-59mXEDBI64jwBpEqfkDARpWmpQcbH9qhwN0PRXhaJ6sCFUMHrvOhH0BvEPlGKhwxOigEraNMRBOKyxEfY_8_JgwuQ5X3Y7T2NZ8szt8g==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-16T10:15:00.000Z", "utc_arrival": "2023-05-16T08:15:00.000Z", "local_departure": "2023-05-16T06:55:00.000Z", "utc_departure": "2023-05-16T04:55:00.000Z"}, {"id": "0b770a224c280000cced2481_0|0a220b774c2b00000a3f7587_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 667.436169, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 196900.1218, "conversion": {"EUR": 515.436549, "HUF": 196900.1218}, "fare": {"adults": 98450.06, "children": 98450.06, "infants": 98450.06}, "bags_price": {"1": 68.306, "2": 136.598}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 4}, "airlines": ["FR"], "route": [{"id": "0b770a224c280000cced2481_0", "combination_id": "0b770a224c280000cced2481", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-19T21:45:00.000Z", "utc_arrival": "2023-05-19T19:45:00.000Z", "local_departure": "2023-05-19T18:25:00.000Z", "utc_departure": "2023-05-19T16:25:00.000Z"}, {"id": "0a220b774c2b00000a3f7587_0", "combination_id": "0a220b774c2b00000a3f7587", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-22T10:15:00.000Z", "utc_arrival": "2023-05-22T08:15:00.000Z", "local_departure": "2023-05-22T07:05:00.000Z", "utc_departure": "2023-05-22T05:05:00.000Z"}], "booking_token": "EuTRRCIXZ6LsgAwlUKXxjtah_DlTDBET_FdD8XQ2iea9nvj9I53XzJgV1m_pVct9YNeNVo_SyiCTkiKaoenLOWMyHcJoS1exjpxRs8NT12vsA36C_YrqpC-_AjpSmU4_Dyc4OElUtJphkNAsPvfKVTL4KroGnaKg9ZR8NN0C4EiNeL5ubGM90_yDbwKtF4lFN3tlQd4TJZdwvCFSb74Gicj3tCXZ_7kgItvc32m3xJj_MfpxJy4SWfk2c2322DHSUOuDoauyDFK29s-9arjCfUv6tIxAKgVX6eaJqGFt0aOQVEXd9ZMK49IgBvvBCef1_k88IBR8rB4gRcMrg19sp71NAbY8ZodfAsqbXKVdHaT31oHBVQeP4xYvS9IMcDyKWCuqFyksl13O4LBhaEsLGirInPAPvFGLxIPap4pfuNpMUf6-zu2euR8Cpfi_wWP-UnSX8c2JY4HG7Q944EsFaWPLuCWXFGMYqryjNdHnEiznFfSnfUVQG7PVWP2t1KllQT0U4TOTLeNssPymNiWDxLF0wBOjS7aBRu3zdq2E53KERIkAJM6EmT9SmLZg9NqVBzvELxLvB4jWSv5QfJXay8-m0vVhzUEMT8uFfzkZXS5H5C5cMNRqmcKH_99G4bk3Bt2j2-cPUVj_fAh1KkNw6L7p-36Ed8BFCE65hgaS-APxmEBV8wUnLizz9IoCl-ckwKsZjqE_bm49e7T4VVob_eWekBul__u-r-l_W8l49UFBf7TmbfSY1QJK9TB-MLy20", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c280000cced2481_0%7C0a220b774c2b00000a3f7587_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EuTRRCIXZ6LsgAwlUKXxjtah_DlTDBET_FdD8XQ2iea9nvj9I53XzJgV1m_pVct9YNeNVo_SyiCTkiKaoenLOWMyHcJoS1exjpxRs8NT12vsA36C_YrqpC-_AjpSmU4_Dyc4OElUtJphkNAsPvfKVTL4KroGnaKg9ZR8NN0C4EiNeL5ubGM90_yDbwKtF4lFN3tlQd4TJZdwvCFSb74Gicj3tCXZ_7kgItvc32m3xJj_MfpxJy4SWfk2c2322DHSUOuDoauyDFK29s-9arjCfUv6tIxAKgVX6eaJqGFt0aOQVEXd9ZMK49IgBvvBCef1_k88IBR8rB4gRcMrg19sp71NAbY8ZodfAsqbXKVdHaT31oHBVQeP4xYvS9IMcDyKWCuqFyksl13O4LBhaEsLGirInPAPvFGLxIPap4pfuNpMUf6-zu2euR8Cpfi_wWP-UnSX8c2JY4HG7Q944EsFaWPLuCWXFGMYqryjNdHnEiznFfSnfUVQG7PVWP2t1KllQT0U4TOTLeNssPymNiWDxLF0wBOjS7aBRu3zdq2E53KERIkAJM6EmT9SmLZg9NqVBzvELxLvB4jWSv5QfJXay8-m0vVhzUEMT8uFfzkZXS5H5C5cMNRqmcKH_99G4bk3Bt2j2-cPUVj_fAh1KkNw6L7p-36Ed8BFCE65hgaS-APxmEBV8wUnLizz9IoCl-ckwKsZjqE_bm49e7T4VVob_eWekBul__u-r-l_W8l49UFBf7TmbfSY1QJK9TB-MLy20", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-19T21:45:00.000Z", "utc_arrival": "2023-05-19T19:45:00.000Z", "local_departure": "2023-05-19T18:25:00.000Z", "utc_departure": "2023-05-19T16:25:00.000Z"}, {"id": "0b770a224c450000d9d313ec_0|0a220b774c4900001ad380d9_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 668.088145, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 197149.1809, "conversion": {"EUR": 516.088525, "HUF": 197149.1809}, "fare": {"adults": 98574.59, "children": 98574.59, "infants": 98574.59}, "bags_price": {"1": 85.554, "2": 180.908}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 158, "hold_height": 52, "hold_length": 78, "hold_weight": 20, "hold_width": 28, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 3, "personal_item_width": 15}, "availability": {"seats": 6}, "airlines": ["FR", "IB"], "route": [{"id": "0b770a224c450000d9d313ec_0", "combination_id": "0b770a224c450000d9d313ec", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-17T13:25:00.000Z", "utc_arrival": "2023-06-17T11:25:00.000Z", "local_departure": "2023-06-17T10:05:00.000Z", "utc_departure": "2023-06-17T08:05:00.000Z"}, {"id": "0a220b774c4900001ad380d9_0", "combination_id": "0a220b774c4900001ad380d9", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "IB", "flight_no": 3278, "operating_carrier": "IB", "operating_flight_no": "3278", "fare_basis": "NWNNAOB4", "fare_category": "M", "fare_classes": "N", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-21T14:55:00.000Z", "utc_arrival": "2023-06-21T12:55:00.000Z", "local_departure": "2023-06-21T11:45:00.000Z", "utc_departure": "2023-06-21T09:45:00.000Z"}], "booking_token": "E1K5XaGWPsDq4byOdYvHW0u3_Qq-S7gm6S7TGNLOzfKf09Pup4QFHOUE1JuWzsQuslE_hwI0YnxklPoun5KVthA7v20YPnBM4GIRNkWrfO0fA3VS75MlXTKJ2hUMfcWNIsocw4MPEXYJlX-Cwjv5CdBPDVqHNFJ41_dEIsvAU573cfb1W4hmtqWByYbHSIiy7LI1CAaQkqNGwoHTWP3W3RaDEl7tX4rMcJuUlreXGLZWtxgLsql2llzNJGeRzRsUbADECQECmR07zTA5j8djLBFkAZWZbNyh_JjBQc8H_Dh19aV28PDdoip7dn_HXogxtTLW0nIT1X2WvWal3ZL43aKFUjfGGzjQjp6U9VgS8yhlliYpLwG3EyD6Cd0jk3kteMKgUtcJOUh-Xs2a46wII-2sDnHpm_u4PiMNWGJX8f4LQ5dimoJO_Z-NxdBRQCwbKkRqeVxjK9_i_EI8qumM1378P5AOPua4zg_Gc2SjQXGcv0_af2b2TFpQrLIAe2NmFgM4dQXWYvp_k7mybHCVVmg8R0r1o2UnPwvxriEYj-3TgzS1CwvMXhkTrt_BMdJeN5DCLXbq59ljzWa5kCRo8TIMr1ib9CDYpHXBuyDKvrxjroWzN_osFc59E2S1HFN5SQshgkpVueCnTQpeppWSrrCb79_jNzLklSdGAOWEVz-NvqNyuHK-bLUD36BJfQvBkKd3ddWYirUqrNqZNDIY5BbZLObeoZVVCmcFe_V0Ut7KCI0-XrsFUO54pTQZnjaMd", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c450000d9d313ec_0%7C0a220b774c4900001ad380d9_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=E1K5XaGWPsDq4byOdYvHW0u3_Qq-S7gm6S7TGNLOzfKf09Pup4QFHOUE1JuWzsQuslE_hwI0YnxklPoun5KVthA7v20YPnBM4GIRNkWrfO0fA3VS75MlXTKJ2hUMfcWNIsocw4MPEXYJlX-Cwjv5CdBPDVqHNFJ41_dEIsvAU573cfb1W4hmtqWByYbHSIiy7LI1CAaQkqNGwoHTWP3W3RaDEl7tX4rMcJuUlreXGLZWtxgLsql2llzNJGeRzRsUbADECQECmR07zTA5j8djLBFkAZWZbNyh_JjBQc8H_Dh19aV28PDdoip7dn_HXogxtTLW0nIT1X2WvWal3ZL43aKFUjfGGzjQjp6U9VgS8yhlliYpLwG3EyD6Cd0jk3kteMKgUtcJOUh-Xs2a46wII-2sDnHpm_u4PiMNWGJX8f4LQ5dimoJO_Z-NxdBRQCwbKkRqeVxjK9_i_EI8qumM1378P5AOPua4zg_Gc2SjQXGcv0_af2b2TFpQrLIAe2NmFgM4dQXWYvp_k7mybHCVVmg8R0r1o2UnPwvxriEYj-3TgzS1CwvMXhkTrt_BMdJeN5DCLXbq59ljzWa5kCRo8TIMr1ib9CDYpHXBuyDKvrxjroWzN_osFc59E2S1HFN5SQshgkpVueCnTQpeppWSrrCb79_jNzLklSdGAOWEVz-NvqNyuHK-bLUD36BJfQvBkKd3ddWYirUqrNqZNDIY5BbZLObeoZVVCmcFe_V0Ut7KCI0-XrsFUO54pTQZnjaMd", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-17T13:25:00.000Z", "utc_arrival": "2023-06-17T11:25:00.000Z", "local_departure": "2023-06-17T10:05:00.000Z", "utc_departure": "2023-06-17T08:05:00.000Z"}, {"id": "0b770a224c270000783de5dc_0|0a220b774c2b00000a3f7587_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 671.216028, "distance": 1975.87, "duration": {"departure": 12600, "return": 11400, "total": 24000}, "price": 197325.3711, "conversion": {"EUR": 516.549748, "HUF": 197325.3711}, "fare": {"adults": 98662.69, "children": 98662.69, "infants": 98662.69}, "bags_price": {"1": 90.804, "2": 181.622}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 2}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224c270000783de5dc_0", "combination_id": "0b770a224c270000783de5dc", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "JKREG", "fare_category": "M", "fare_classes": "J", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-18T21:15:00.000Z", "utc_arrival": "2023-05-18T19:15:00.000Z", "local_departure": "2023-05-18T17:45:00.000Z", "utc_departure": "2023-05-18T15:45:00.000Z"}, {"id": "0a220b774c2b00000a3f7587_0", "combination_id": "0a220b774c2b00000a3f7587", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-22T10:15:00.000Z", "utc_arrival": "2023-05-22T08:15:00.000Z", "local_departure": "2023-05-22T07:05:00.000Z", "utc_departure": "2023-05-22T05:05:00.000Z"}], "booking_token": "ER1pTCzLAu8-1LBMyweKBM7JDYy5018HuMQSquGTe14YLyOkZp5Bhae_LbO5-WIdqiflNTvgyC04-AlGE5gZrsp_AOa08xm-S0QmUqZ6gPe6kFJcGr1EImHskimm9z1IKBJL90alfF0oepn0yVoTvoNhkzWV56YCWYNMf6oMiPqu9WdSTZ4FTnMdQ8mmPhSCYIEwfYl3ionOYY9PlZHtxRm40XqQbrUBZjF9kdDr0gxglcy6vHAeMwf-46F95q9zngiCMBQxGwIrUTuH2rR_eXe7GNNYY5-TCwKYSXOUJKn_3e6L6s3cs4PRDSUy8jRC6cUN_svK6Q1lnls9T_PYlHPQFzOHa2AJqGxsG5dN2_lCox2A8zj-d5y14NJ1zqVMAJrViMOhglTUjUshprrSRFfShnbxRJHI_JDTqJmwV6s-NiMBd5_n9AlkG5bcaujvXapaSf0emyzJ16hmtL9ImLFEYpNr_0i8FpTO4m_Clg83uKNCEyyRiKD5K0YcPqB6Qme8YCXX7v2N7UpXdckEzRe-NMDZN4hgAIlIbvnMGijgN3gkGTNUJPAtTyfk6mdIVW3qac5kP41NT8yAYRI38bgHBpbJnXmmTR6g-numX7mBWhgTY7h7GTip9GWwyQPScCwQ0KCev9yf3lMhOKnRiMVzg7ojHQKSrxrx0q3I_6Fs5IrdlP4E6Sz98lfmZbxRsF3-UJIhr7FmxDa9zIWINDSP-lwbciXnBcQnKq0uOKVb4R-CmYKLCjbexx_FymSqQyt1pc8YTyEpu2SGOIdUCMZhZ2-ccUJ_jBxgMW-LErdk=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c270000783de5dc_0%7C0a220b774c2b00000a3f7587_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=ER1pTCzLAu8-1LBMyweKBM7JDYy5018HuMQSquGTe14YLyOkZp5Bhae_LbO5-WIdqiflNTvgyC04-AlGE5gZrsp_AOa08xm-S0QmUqZ6gPe6kFJcGr1EImHskimm9z1IKBJL90alfF0oepn0yVoTvoNhkzWV56YCWYNMf6oMiPqu9WdSTZ4FTnMdQ8mmPhSCYIEwfYl3ionOYY9PlZHtxRm40XqQbrUBZjF9kdDr0gxglcy6vHAeMwf-46F95q9zngiCMBQxGwIrUTuH2rR_eXe7GNNYY5-TCwKYSXOUJKn_3e6L6s3cs4PRDSUy8jRC6cUN_svK6Q1lnls9T_PYlHPQFzOHa2AJqGxsG5dN2_lCox2A8zj-d5y14NJ1zqVMAJrViMOhglTUjUshprrSRFfShnbxRJHI_JDTqJmwV6s-NiMBd5_n9AlkG5bcaujvXapaSf0emyzJ16hmtL9ImLFEYpNr_0i8FpTO4m_Clg83uKNCEyyRiKD5K0YcPqB6Qme8YCXX7v2N7UpXdckEzRe-NMDZN4hgAIlIbvnMGijgN3gkGTNUJPAtTyfk6mdIVW3qac5kP41NT8yAYRI38bgHBpbJnXmmTR6g-numX7mBWhgTY7h7GTip9GWwyQPScCwQ0KCev9yf3lMhOKnRiMVzg7ojHQKSrxrx0q3I_6Fs5IrdlP4E6Sz98lfmZbxRsF3-UJIhr7FmxDa9zIWINDSP-lwbciXnBcQnKq0uOKVb4R-CmYKLCjbexx_FymSqQyt1pc8YTyEpu2SGOIdUCMZhZ2-ccUJ_jBxgMW-LErdk=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-18T21:15:00.000Z", "utc_arrival": "2023-05-18T19:15:00.000Z", "local_departure": "2023-05-18T17:45:00.000Z", "utc_departure": "2023-05-18T15:45:00.000Z"}, {"id": "0b770a224c470000e38f46b1_0|0a220b774c4b0000292d2891_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 669.391742, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 197647.1635, "conversion": {"EUR": 517.392122, "HUF": 197647.1635}, "fare": {"adults": 98823.58, "children": 98823.58, "infants": 98823.58}, "bags_price": {"1": 78.078, "2": 156.142}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 4}, "airlines": ["FR"], "route": [{"id": "0b770a224c470000e38f46b1_0", "combination_id": "0b770a224c470000e38f46b1", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-19T14:00:00.000Z", "utc_arrival": "2023-06-19T12:00:00.000Z", "local_departure": "2023-06-19T10:40:00.000Z", "utc_departure": "2023-06-19T08:40:00.000Z"}, {"id": "0a220b774c4b0000292d2891_0", "combination_id": "0a220b774c4b0000292d2891", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-23T18:00:00.000Z", "utc_arrival": "2023-06-23T16:00:00.000Z", "local_departure": "2023-06-23T14:50:00.000Z", "utc_departure": "2023-06-23T12:50:00.000Z"}], "booking_token": "EmHM8rPfFBtXEXfma_71QOISC76zAZOcZEcMXAsZHvtx4Bia8PGup4x_JUC4JxVWzxHL6jgrgjC5M_vM2eeKponNMuJEPBMAInqQLZeEV4Q_mGsH0kEeu1dCnAT3OwiCgcHma4sRxPyLVlNvbGcB6kLA0602U186v_Fh9t28UfXwFL2YVnuD7Byp3P919dkCIdwqGZWiIkKUUH2ddDzB4u1x1HotFN_sGzBIMncOA1KRoOapQpq3leqU_ItOprR5ktuFgY1pIUg3CzoJHSeMH5XLV5_N-3RHqjowFKV_qdgiiFmJFRPzFFb9QNWsnVvIb3oC7cQH6Wc1-1-nX_ahbbNPl4u_47MpKlwcCnZuil30YeNxbWVkbyn3qfJBYv8ouVV4d32YV3lVCPt3GArAJXaDDnLluuLbvbvoEy4cl_RxPox_-uXKOrrxi7C40xzW-BC-8qOFWyPgO770GNP_rlOPeYWuPbcCjRUOWu6rDOlQvvQ47_BbcGWEQll-AnKFX9V51ysbLmzuZ1_soIjMjKMuC9Ghh3uZw8udfG4y0hjuVM140NAK6UDVZo35S3VMJx-wov9uWd48K1Qz6yksU0c1CwPCB9AAfphHQwANZVQjKC15PxD9PM1zre291ocGWgcw57dt6dfHTY0uInKwY9Dm3fiEXNbeJhqJRLt9H2dZjev54BC2ZsUIDhEgNnGYrz9SD1jwPDAerJA2KMDNqC1jbep8E5sXdfr4LVc_vFFiw5AFGCBWmj6iNhbvypGks", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c470000e38f46b1_0%7C0a220b774c4b0000292d2891_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EmHM8rPfFBtXEXfma_71QOISC76zAZOcZEcMXAsZHvtx4Bia8PGup4x_JUC4JxVWzxHL6jgrgjC5M_vM2eeKponNMuJEPBMAInqQLZeEV4Q_mGsH0kEeu1dCnAT3OwiCgcHma4sRxPyLVlNvbGcB6kLA0602U186v_Fh9t28UfXwFL2YVnuD7Byp3P919dkCIdwqGZWiIkKUUH2ddDzB4u1x1HotFN_sGzBIMncOA1KRoOapQpq3leqU_ItOprR5ktuFgY1pIUg3CzoJHSeMH5XLV5_N-3RHqjowFKV_qdgiiFmJFRPzFFb9QNWsnVvIb3oC7cQH6Wc1-1-nX_ahbbNPl4u_47MpKlwcCnZuil30YeNxbWVkbyn3qfJBYv8ouVV4d32YV3lVCPt3GArAJXaDDnLluuLbvbvoEy4cl_RxPox_-uXKOrrxi7C40xzW-BC-8qOFWyPgO770GNP_rlOPeYWuPbcCjRUOWu6rDOlQvvQ47_BbcGWEQll-AnKFX9V51ysbLmzuZ1_soIjMjKMuC9Ghh3uZw8udfG4y0hjuVM140NAK6UDVZo35S3VMJx-wov9uWd48K1Qz6yksU0c1CwPCB9AAfphHQwANZVQjKC15PxD9PM1zre291ocGWgcw57dt6dfHTY0uInKwY9Dm3fiEXNbeJhqJRLt9H2dZjev54BC2ZsUIDhEgNnGYrz9SD1jwPDAerJA2KMDNqC1jbep8E5sXdfr4LVc_vFFiw5AFGCBWmj6iNhbvypGks", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-19T14:00:00.000Z", "utc_arrival": "2023-06-19T12:00:00.000Z", "local_departure": "2023-06-19T10:40:00.000Z", "utc_departure": "2023-06-19T08:40:00.000Z"}, {"id": "0b770a224c280000cced2481_0|0a220b774c2c000089e7df3d_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 671.242012, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 198353.9787, "conversion": {"EUR": 519.242392, "HUF": 198353.9787}, "fare": {"adults": 99176.99, "children": 99176.99, "infants": 99176.99}, "bags_price": {"1": 69.678, "2": 139.356}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 6}, "airlines": ["FR"], "route": [{"id": "0b770a224c280000cced2481_0", "combination_id": "0b770a224c280000cced2481", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-19T21:45:00.000Z", "utc_arrival": "2023-05-19T19:45:00.000Z", "local_departure": "2023-05-19T18:25:00.000Z", "utc_departure": "2023-05-19T16:25:00.000Z"}, {"id": "0a220b774c2c000089e7df3d_0", "combination_id": "0a220b774c2c000089e7df3d", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-23T14:05:00.000Z", "utc_arrival": "2023-05-23T12:05:00.000Z", "local_departure": "2023-05-23T10:55:00.000Z", "utc_departure": "2023-05-23T08:55:00.000Z"}], "booking_token": "EbWueDYmJzDCXhtmmbDd04IkXwKZEop19F4TaSQabsTCU2h3NZ1KyrIr7vPO1kP5NpjOlB1NroFeJ_zRqDRH9GFynus7JuF30qStBxgKqrYA1fzmKX__4YmqLDRUxqfXLZeEK1oOpNjZxDHXt4FKM0kwRTp1FwrDRprV4qisUjI0ai91KhHJX8luwJcsJG0eTQzsONN01gUuCMi_gllqNT70N4UM32JcTarLlseQbneFWhAtZTV9tAzWWcKrRxubVNIGlCZ4rL7QwwJ5R2IWIXXnD-itk0F0DUuOYuK_f8_JgC5BC246Btr2m3cyySMzhXsHrphPp42mfkjKzauqVF8JxciSVvDd6Rrkzyo2wOg-Nz-OkxyDWKiA6d1G4_IKsiwP9aN2BwNean1Kow8JLQiX1fhpSAwWudQv8kLTHcYx_RnfR8wWi9FCLGBTqjmN4prqe_WtgRc_i_qOHJ8-z37n5ln7AmZuR8OWnk9l_Ev-Gxa9LHPTgfiEis_QMdo8qYSw2DSuabvGpPEsO7SWzLsy8Bmn00T6zsttf1v8pD5V4PSrqYVt_8dUD7WSMg-Ru2q_7ugm1dvGfVpsiyyED0ZAKuHa1Iak9EMR2pCYctNX4kFnfGoUndeaba6hVAZXzOV7pUE2QHSC0Go3DbmEMjB5751padWwC5INYU9tfL7eYCyN0SoZftHVZQd-mW9nsGh8_ofAovlycuOBuc-Qh1DajkBxSzEF8jBPTtKYf3XY=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c280000cced2481_0%7C0a220b774c2c000089e7df3d_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EbWueDYmJzDCXhtmmbDd04IkXwKZEop19F4TaSQabsTCU2h3NZ1KyrIr7vPO1kP5NpjOlB1NroFeJ_zRqDRH9GFynus7JuF30qStBxgKqrYA1fzmKX__4YmqLDRUxqfXLZeEK1oOpNjZxDHXt4FKM0kwRTp1FwrDRprV4qisUjI0ai91KhHJX8luwJcsJG0eTQzsONN01gUuCMi_gllqNT70N4UM32JcTarLlseQbneFWhAtZTV9tAzWWcKrRxubVNIGlCZ4rL7QwwJ5R2IWIXXnD-itk0F0DUuOYuK_f8_JgC5BC246Btr2m3cyySMzhXsHrphPp42mfkjKzauqVF8JxciSVvDd6Rrkzyo2wOg-Nz-OkxyDWKiA6d1G4_IKsiwP9aN2BwNean1Kow8JLQiX1fhpSAwWudQv8kLTHcYx_RnfR8wWi9FCLGBTqjmN4prqe_WtgRc_i_qOHJ8-z37n5ln7AmZuR8OWnk9l_Ev-Gxa9LHPTgfiEis_QMdo8qYSw2DSuabvGpPEsO7SWzLsy8Bmn00T6zsttf1v8pD5V4PSrqYVt_8dUD7WSMg-Ru2q_7ugm1dvGfVpsiyyED0ZAKuHa1Iak9EMR2pCYctNX4kFnfGoUndeaba6hVAZXzOV7pUE2QHSC0Go3DbmEMjB5751padWwC5INYU9tfL7eYCyN0SoZftHVZQd-mW9nsGh8_ofAovlycuOBuc-Qh1DajkBxSzEF8jBPTtKYf3XY=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-19T21:45:00.000Z", "utc_arrival": "2023-05-19T19:45:00.000Z", "local_departure": "2023-05-19T18:25:00.000Z", "utc_departure": "2023-05-19T16:25:00.000Z"}, {"id": "0b770a224bef0000e50ad4c9_0|0a220b774bf200002286f566_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 673.709015, "distance": 1975.87, "duration": {"departure": 12000, "return": 11700, "total": 23700}, "price": 198787.0492, "conversion": {"EUR": 520.376065, "HUF": 198787.0492}, "fare": {"adults": 99393.52, "children": 99393.52, "infants": 99393.52}, "bags_price": {"1": 88.06, "2": 176.12}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 2}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224bef0000e50ad4c9_0", "combination_id": "0b770a224bef0000e50ad4c9", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-03-23T13:40:00.000Z", "utc_arrival": "2023-03-23T12:40:00.000Z", "local_departure": "2023-03-23T10:20:00.000Z", "utc_departure": "2023-03-23T09:20:00.000Z"}, {"id": "0a220b774bf200002286f566_0", "combination_id": "0a220b774bf200002286f566", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IJREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-03-26T21:05:00.000Z", "utc_arrival": "2023-03-26T19:05:00.000Z", "local_departure": "2023-03-26T17:50:00.000Z", "utc_departure": "2023-03-26T15:50:00.000Z"}], "booking_token": "EXcCn73moK5rny_FBikHy9OHfef7wIRwjABPEHa3xzkJzx6C4aX0rcv_0PImHggDKku81nl1-_PyD_3abyYmxUspkxSCxGpQNbsMyxSx0r5KBhY6DEPRwHW0qoB1pJCDGjLe6JpLzPxL0hhXazxP4DQinhYuqFVfRjVUlIFWR7qEJAWdxLPW2IxwKbHumu1OnpKAFx3foAtqVxbGfIpVAYXMHYL_KME3ZIyORxeWt0v3LN2e5DBTDG0LuySvkrjZS5rLDoJBGckE-yV4T8zU4jkmVHZzxj0E7Y5sRDyFAlrtVY0Y7NKUSTo1rmlUo4_q94CxkNrzl58_LV-3B7srPJaNwo4JpwOgTbmygzZNgSobRj4m8_ynYd-W4eR4Ywbudd5ukGy5Yd6t8jAzAFvS0Q51515f5Z6E2dEi9gtg8q37SOmlVd06jKHq1lfymfNhWBycQYCnQmWj8K8ewh7fMVNg6RM6oGB5X8456vPzrOVIBrRwyIYfvRNL75f0O3Kgu-Lj2AIolYdDMDkNa8Oald6ISiz6gUNFRqVVQa_nexLa_VSsl95cJR3QONBK-ZYxpL1jSLmy59ZXhcVz6Kc1KlO4Q7ILeW7BGlX8ZO-HxgxE9jQWQTSYsHX5ONpN6tqzdHMhvwOXIpyFeueUCGcenKr6dHbE2pNZDkGTNyYU-1R2cedPLi13gVjA1rA7mlg9p-XPT-E8Jm9N2DGNqMrtx_Gk8mouv6cSJ8Gzpt1RE9EE8cxSZNR0tdeClKMxbwGA6iUuW8PislYapwqwE47x53FSfn1ida_nIZjf7cDzm8Ow=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224bef0000e50ad4c9_0%7C0a220b774bf200002286f566_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EXcCn73moK5rny_FBikHy9OHfef7wIRwjABPEHa3xzkJzx6C4aX0rcv_0PImHggDKku81nl1-_PyD_3abyYmxUspkxSCxGpQNbsMyxSx0r5KBhY6DEPRwHW0qoB1pJCDGjLe6JpLzPxL0hhXazxP4DQinhYuqFVfRjVUlIFWR7qEJAWdxLPW2IxwKbHumu1OnpKAFx3foAtqVxbGfIpVAYXMHYL_KME3ZIyORxeWt0v3LN2e5DBTDG0LuySvkrjZS5rLDoJBGckE-yV4T8zU4jkmVHZzxj0E7Y5sRDyFAlrtVY0Y7NKUSTo1rmlUo4_q94CxkNrzl58_LV-3B7srPJaNwo4JpwOgTbmygzZNgSobRj4m8_ynYd-W4eR4Ywbudd5ukGy5Yd6t8jAzAFvS0Q51515f5Z6E2dEi9gtg8q37SOmlVd06jKHq1lfymfNhWBycQYCnQmWj8K8ewh7fMVNg6RM6oGB5X8456vPzrOVIBrRwyIYfvRNL75f0O3Kgu-Lj2AIolYdDMDkNa8Oald6ISiz6gUNFRqVVQa_nexLa_VSsl95cJR3QONBK-ZYxpL1jSLmy59ZXhcVz6Kc1KlO4Q7ILeW7BGlX8ZO-HxgxE9jQWQTSYsHX5ONpN6tqzdHMhvwOXIpyFeueUCGcenKr6dHbE2pNZDkGTNyYU-1R2cedPLi13gVjA1rA7mlg9p-XPT-E8Jm9N2DGNqMrtx_Gk8mouv6cSJ8Gzpt1RE9EE8cxSZNR0tdeClKMxbwGA6iUuW8PislYapwqwE47x53FSfn1ida_nIZjf7cDzm8Ow=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-03-23T13:40:00.000Z", "utc_arrival": "2023-03-23T12:40:00.000Z", "local_departure": "2023-03-23T10:20:00.000Z", "utc_departure": "2023-03-23T09:20:00.000Z"}, {"id": "0b770a224c420000e2660c77_0|0a220b774c450000a94cee25_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 671.310466, "distance": 1975.87, "duration": {"departure": 11700, "return": 11400, "total": 23100}, "price": 198889.4693, "conversion": {"EUR": 520.644176, "HUF": 198889.4693}, "fare": {"adults": 99444.73, "children": 99444.73, "infants": 99444.73}, "bags_price": {"1": 76.286, "2": 162.372}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 158, "hold_height": 52, "hold_length": 78, "hold_weight": 20, "hold_width": 28, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 3, "personal_item_width": 15}, "availability": {"seats": 2}, "airlines": ["FR", "IB"], "route": [{"id": "0b770a224c420000e2660c77_0", "combination_id": "0b770a224c420000e2660c77", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "IB", "flight_no": 3279, "operating_carrier": "IB", "operating_flight_no": "3279", "fare_basis": "NZNNAOB4", "fare_category": "M", "fare_classes": "N", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-14T18:50:00.000Z", "utc_arrival": "2023-06-14T16:50:00.000Z", "local_departure": "2023-06-14T15:35:00.000Z", "utc_departure": "2023-06-14T13:35:00.000Z"}, {"id": "0a220b774c450000a94cee25_0", "combination_id": "0a220b774c450000a94cee25", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-17T09:40:00.000Z", "utc_arrival": "2023-06-17T07:40:00.000Z", "local_departure": "2023-06-17T06:30:00.000Z", "utc_departure": "2023-06-17T04:30:00.000Z"}], "booking_token": "ED5o0IBkfLuBZ400dHB4-QmHTlrqiNe4SYmCrTxWnYFhHMpVgP8TdQb4zga6qVtDEbpX3KmgpIMQ4Fp__CKiAbbyt_ZW32nf7yxsuG5G31LYa6bTJaV8r4Pd_JLRCi3o2NE0pFp1mAHmW4g-rIgjOAmHj5S1WWnj-NkpkjerTueBxCk-k7x07ko6aiv50R44FCPqOvFUBGdzjL9VrW0GekVepHDbcRP8gXNfS2q7msPkgCRkoc5kk_lmQ4-WVa6AINAMsdcXcg9By0G1mTWmWZDHMI-pBt4Rx2Gr7D-klndlmwQ7jNkDXs1FKgxEQ4aeu623JAUBSUG54SjR6RHwfdyjO_QXnOuLAQhOTkU6WfG_5E5qihU51YIAUevg99BL-177NKT6g7vsWlPr4FhvqiHmkfcbu9dhrkZXYsMv9hiTCMnEyKJ-qqNqMKRS4yjfxD5TpaOp871dZC5h34qdhWAGH72aj9CxiyDriNfquLd21b76qKAfSN0iynd0cgWd6waOspNnVOcJZxy1b0H7LzbhBIyidUr49j2HO2Dm98U51lrjmSYx4x-RZys7vg0VX35gHOdgu02ldmWY58UorwC85XC_gUMOoJKajBmOdzzw7RASKG7Sv940cDPP9HjtPMIpuGQmfhwEO0s0uOtZR5J98rLNpI3gkAo7fQbtulG-nZsz7ReT-ISEmnKiyyaFtAye7x7BvZfywbradu0Xr_W_Khob2bj9XmARxF_QA35k=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c420000e2660c77_0%7C0a220b774c450000a94cee25_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=ED5o0IBkfLuBZ400dHB4-QmHTlrqiNe4SYmCrTxWnYFhHMpVgP8TdQb4zga6qVtDEbpX3KmgpIMQ4Fp__CKiAbbyt_ZW32nf7yxsuG5G31LYa6bTJaV8r4Pd_JLRCi3o2NE0pFp1mAHmW4g-rIgjOAmHj5S1WWnj-NkpkjerTueBxCk-k7x07ko6aiv50R44FCPqOvFUBGdzjL9VrW0GekVepHDbcRP8gXNfS2q7msPkgCRkoc5kk_lmQ4-WVa6AINAMsdcXcg9By0G1mTWmWZDHMI-pBt4Rx2Gr7D-klndlmwQ7jNkDXs1FKgxEQ4aeu623JAUBSUG54SjR6RHwfdyjO_QXnOuLAQhOTkU6WfG_5E5qihU51YIAUevg99BL-177NKT6g7vsWlPr4FhvqiHmkfcbu9dhrkZXYsMv9hiTCMnEyKJ-qqNqMKRS4yjfxD5TpaOp871dZC5h34qdhWAGH72aj9CxiyDriNfquLd21b76qKAfSN0iynd0cgWd6waOspNnVOcJZxy1b0H7LzbhBIyidUr49j2HO2Dm98U51lrjmSYx4x-RZys7vg0VX35gHOdgu02ldmWY58UorwC85XC_gUMOoJKajBmOdzzw7RASKG7Sv940cDPP9HjtPMIpuGQmfhwEO0s0uOtZR5J98rLNpI3gkAo7fQbtulG-nZsz7ReT-ISEmnKiyyaFtAye7x7BvZfywbradu0Xr_W_Khob2bj9XmARxF_QA35k=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-14T18:50:00.000Z", "utc_arrival": "2023-06-14T16:50:00.000Z", "local_departure": "2023-06-14T15:35:00.000Z", "utc_departure": "2023-06-14T13:35:00.000Z"}, {"id": "0b770a224c490000960764e7_0|0a220b774c4c0000b6fa7a34_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 672.07099, "distance": 1975.87, "duration": {"departure": 11700, "return": 11400, "total": 23100}, "price": 199179.9944, "conversion": {"EUR": 521.4047, "HUF": 199179.9944}, "fare": {"adults": 99590, "children": 104973.24, "infants": 104973.24}, "bags_price": {"1": 77.686, "2": 165.172}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 158, "hold_height": 52, "hold_length": 78, "hold_weight": 20, "hold_width": 28, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 3, "personal_item_width": 15}, "availability": {"seats": 4}, "airlines": ["FR", "IB"], "route": [{"id": "0b770a224c490000960764e7_0", "combination_id": "0b770a224c490000960764e7", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "IB", "flight_no": 3279, "operating_carrier": "IB", "operating_flight_no": "3279", "fare_basis": "QDNNAOB4", "fare_category": "M", "fare_classes": "Q", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-21T18:50:00.000Z", "utc_arrival": "2023-06-21T16:50:00.000Z", "local_departure": "2023-06-21T15:35:00.000Z", "utc_departure": "2023-06-21T13:35:00.000Z"}, {"id": "0a220b774c4c0000b6fa7a34_0", "combination_id": "0a220b774c4c0000b6fa7a34", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-24T09:40:00.000Z", "utc_arrival": "2023-06-24T07:40:00.000Z", "local_departure": "2023-06-24T06:30:00.000Z", "utc_departure": "2023-06-24T04:30:00.000Z"}], "booking_token": "Ek23HC7_esApHB-sZjleSH_6fN2LwYX4H_8xkQwBkTJd2e2vZDxbx4IZF1XyuVyKbmpZSQUWqPnSfaRMztwmaIa0UMQ1SYal4v4cCJuISy4wQDYqCEy5KXK-ehijsq4LaN81SWoXbhi3pNyt_aZgvz3OrQs_ollROyv54RcL1xSk7F4Ovdqg3o4Z0_387w8LpmA_Oxdfei-zNgu1nZZ1KXgpRVEKm_jEhuDW9j1y89KXucOHEmaiP-0tPYu0vbArKX6sLFMrWu7RB_FhkPt5l2bv3KF0AMMOGpC8-NlUME4KmHWTarHS7hBLJosFmOWg8O5WMqxrfsp4y2g57MnLcUBJVD01oxHWIhanbX5Y4xp_CB4sScxeH-KZyNjGnLq4-2DPhRBP8PgXoxVpHLf23FadljCegcPwKRb9xBHB_6etVYmMO3u1L-iQZOO18munpZAII3yvuo0lbbVT2n7RgEfTbzACLCkADgiIuHP8sKKKIv8n3p9xNRteNc4jZa-qUu7HTm90r4paqUkuKnSg2xeSntA4dT0U3nRlTgI5fAi1gWQvKJ_zKj5olIrrE8tALDIzi89vJS1r68UCuR0bqkoggkjky6671kuKTCc-SOSDwJqGjcTtVBjH7Wdeo3Z2xC0TZeFPZnsbqm6UAKqxntpTuJmZmEFBj-ej_pBHD8yYWjbWQiwUI7alKOIrouvDIQGF0g5-4bmLjqA5S1a3CGpz6IsNVxQqgP4JP_3pQARycwWxQ-3hn2-2e9QT-hLYDZ4Tj7EXKskZXX6AMlppr6JVbpz-gutvmTY6y5wNgaf0=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c490000960764e7_0%7C0a220b774c4c0000b6fa7a34_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=Ek23HC7_esApHB-sZjleSH_6fN2LwYX4H_8xkQwBkTJd2e2vZDxbx4IZF1XyuVyKbmpZSQUWqPnSfaRMztwmaIa0UMQ1SYal4v4cCJuISy4wQDYqCEy5KXK-ehijsq4LaN81SWoXbhi3pNyt_aZgvz3OrQs_ollROyv54RcL1xSk7F4Ovdqg3o4Z0_387w8LpmA_Oxdfei-zNgu1nZZ1KXgpRVEKm_jEhuDW9j1y89KXucOHEmaiP-0tPYu0vbArKX6sLFMrWu7RB_FhkPt5l2bv3KF0AMMOGpC8-NlUME4KmHWTarHS7hBLJosFmOWg8O5WMqxrfsp4y2g57MnLcUBJVD01oxHWIhanbX5Y4xp_CB4sScxeH-KZyNjGnLq4-2DPhRBP8PgXoxVpHLf23FadljCegcPwKRb9xBHB_6etVYmMO3u1L-iQZOO18munpZAII3yvuo0lbbVT2n7RgEfTbzACLCkADgiIuHP8sKKKIv8n3p9xNRteNc4jZa-qUu7HTm90r4paqUkuKnSg2xeSntA4dT0U3nRlTgI5fAi1gWQvKJ_zKj5olIrrE8tALDIzi89vJS1r68UCuR0bqkoggkjky6671kuKTCc-SOSDwJqGjcTtVBjH7Wdeo3Z2xC0TZeFPZnsbqm6UAKqxntpTuJmZmEFBj-ej_pBHD8yYWjbWQiwUI7alKOIrouvDIQGF0g5-4bmLjqA5S1a3CGpz6IsNVxQqgP4JP_3pQARycwWxQ-3hn2-2e9QT-hLYDZ4Tj7EXKskZXX6AMlppr6JVbpz-gutvmTY6y5wNgaf0=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-21T18:50:00.000Z", "utc_arrival": "2023-06-21T16:50:00.000Z", "local_departure": "2023-06-21T15:35:00.000Z", "utc_departure": "2023-06-21T13:35:00.000Z"}, {"id": "0b770a224c3c0000c3c77655_0|0a220b774c40000011657e80_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 676.55799, "distance": 1975.87, "duration": {"departure": 12600, "return": 11400, "total": 24000}, "price": 199366.0354, "conversion": {"EUR": 521.89171, "HUF": 199366.0354}, "fare": {"adults": 99683.02, "children": 103197.2, "infants": 103197.2}, "bags_price": {"1": 91.21, "2": 182.42}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 6}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224c3c0000c3c77655_0", "combination_id": "0b770a224c3c0000c3c77655", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "HIREG", "fare_category": "M", "fare_classes": "H", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-08T21:15:00.000Z", "utc_arrival": "2023-06-08T19:15:00.000Z", "local_departure": "2023-06-08T17:45:00.000Z", "utc_departure": "2023-06-08T15:45:00.000Z"}, {"id": "0a220b774c40000011657e80_0", "combination_id": "0a220b774c40000011657e80", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-12T10:15:00.000Z", "utc_arrival": "2023-06-12T08:15:00.000Z", "local_departure": "2023-06-12T07:05:00.000Z", "utc_departure": "2023-06-12T05:05:00.000Z"}], "booking_token": "ER3-kqBAFNy6RLqtiY8iEL0QHZ9khlzhbjTfhKIiiDGfcDL8HmuIjTslhY9t0xc0TWbQnUISSIe8VHcR9F4Y8WDzWTSpa4zB3Hcw8tGCsEIta0pZxPlkYUSivyc8UliFAwjvraeznQiB_qifsE0VZEsWELKaC2-Lt8373Ev0lrN0TBvbf9Ypqm9L8I21qs3hkZyqrpFcQJd0Ws4QnLUD8l2JMwzKJSaMS4lJj-cKaEy8kUMCRqZUJrJVAxOrQgRebJwxmOCFmYN51b1DEBoDCxpxVcoNZDmPQMs9D1KcowClxoJIbbd-EdyqyqIJsYepgyUQrZ8PpErDVie_-W71YTAaJlCHt3h3p5g3xL6OhJjtngoeSV2PepxGgYRvDNaCKTrtNHJebBAvKGr-hMcweuMXJJji8bQyQp0B8rqkaWKNOxJGDEK-irW0XRHTYwVBl90bqqZWrEXH6cPCIc9I7Rj2vf1IO9RZPjj58R2xD9XYRYxOkYo2iGdAuU2u2jqPrFSVrAvZ-Jsupu2XrsT2bBkoT7QRbowTz8rDGhA2sE-VCQuQBnzKpE-7lujwWBIpcZlGUGkZtdvE0JHR0EDjThWbZuE3DsD9yBFrJhca8uaZaPdko8Kuauad2T2Vr-Z4Zk_J0egDTcm6IdvJh8IhVYL4jR9WT4_ZsFURssyOmk2kr6MPxQwKLlfLurv8saagEtgHPwX_r8nvFdfBjLwxYMoxqtahofbr9YQbW65mNXbHiXTQ6V7-rwj2GoM5PkjzIxt-7eW6p_aRQzAUYml4gcIEIjx3KDyK2eq21nsqnVG0=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c3c0000c3c77655_0%7C0a220b774c40000011657e80_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=ER3-kqBAFNy6RLqtiY8iEL0QHZ9khlzhbjTfhKIiiDGfcDL8HmuIjTslhY9t0xc0TWbQnUISSIe8VHcR9F4Y8WDzWTSpa4zB3Hcw8tGCsEIta0pZxPlkYUSivyc8UliFAwjvraeznQiB_qifsE0VZEsWELKaC2-Lt8373Ev0lrN0TBvbf9Ypqm9L8I21qs3hkZyqrpFcQJd0Ws4QnLUD8l2JMwzKJSaMS4lJj-cKaEy8kUMCRqZUJrJVAxOrQgRebJwxmOCFmYN51b1DEBoDCxpxVcoNZDmPQMs9D1KcowClxoJIbbd-EdyqyqIJsYepgyUQrZ8PpErDVie_-W71YTAaJlCHt3h3p5g3xL6OhJjtngoeSV2PepxGgYRvDNaCKTrtNHJebBAvKGr-hMcweuMXJJji8bQyQp0B8rqkaWKNOxJGDEK-irW0XRHTYwVBl90bqqZWrEXH6cPCIc9I7Rj2vf1IO9RZPjj58R2xD9XYRYxOkYo2iGdAuU2u2jqPrFSVrAvZ-Jsupu2XrsT2bBkoT7QRbowTz8rDGhA2sE-VCQuQBnzKpE-7lujwWBIpcZlGUGkZtdvE0JHR0EDjThWbZuE3DsD9yBFrJhca8uaZaPdko8Kuauad2T2Vr-Z4Zk_J0egDTcm6IdvJh8IhVYL4jR9WT4_ZsFURssyOmk2kr6MPxQwKLlfLurv8saagEtgHPwX_r8nvFdfBjLwxYMoxqtahofbr9YQbW65mNXbHiXTQ6V7-rwj2GoM5PkjzIxt-7eW6p_aRQzAUYml4gcIEIjx3KDyK2eq21nsqnVG0=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-08T21:15:00.000Z", "utc_arrival": "2023-06-08T19:15:00.000Z", "local_departure": "2023-06-08T17:45:00.000Z", "utc_departure": "2023-06-08T15:45:00.000Z"}, {"id": "0b770a224bee000038feff2a_0|0a220b774bf200002286f566_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 675.272846, "distance": 1975.87, "duration": {"departure": 12000, "return": 11700, "total": 23700}, "price": 199384.4428, "conversion": {"EUR": 521.939896, "HUF": 199384.4428}, "fare": {"adults": 99692.22, "children": 99692.22, "infants": 99692.22}, "bags_price": {"1": 86.688, "2": 173.362}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 6}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224bee000038feff2a_0", "combination_id": "0b770a224bee000038feff2a", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-03-22T23:20:00.000Z", "utc_arrival": "2023-03-22T22:20:00.000Z", "local_departure": "2023-03-22T20:00:00.000Z", "utc_departure": "2023-03-22T19:00:00.000Z"}, {"id": "0a220b774bf200002286f566_0", "combination_id": "0a220b774bf200002286f566", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IJREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-03-26T21:05:00.000Z", "utc_arrival": "2023-03-26T19:05:00.000Z", "local_departure": "2023-03-26T17:50:00.000Z", "utc_departure": "2023-03-26T15:50:00.000Z"}], "booking_token": "EcgFh32snNZLRxn03KziAzp6-1bJlWafHXqpDReDNxg3WN9X_JwVjgCksGu4UGz1HvFcTMoUlrX4OF2y00TZUT1qvto9zKpH8o1FnYulCYilf7K4mJ1OvToxMIY5UEC3kCbFs40jTyuUrMwDGYPhP-nav2JO_cb5EBxGVPndUwFBa3RFZWDMcG_tl0YDek3_RYKUS8PlU9JVR6ggyhtIOenZkVija-WcGz2U_Tmq3R9E91uYu-OIDpzjEEFnyhozTgl4UCa7zWUWFR1_9QcISO8eHeNjI42J9Rhn8PYgpvCmpxndKjXCuiz7BgJ1G7Aw7Npy5URjebp8Ed5EhTt8ASf2eqItr-YUe9eND11Pde2zx3uvG6bnXVQ4CvBuOJqecEfwURiSkvKL7bVBBkjTm9JEBVGqE8fpl_MAUkt1uGDVIJin1242k8QCLaTAfeMYV5av-lKenLzlzhytDI6SxxLN-rBPhmXM03JSOx_zjNLadix36SFwqaVowTyl76XBdsgs67_EWw_7vfOtMU_NBfOXEZ2Vw0ZamzFDoHeA7oOj6IXNyt-kOfcBqxuq3A0LvOc8-SM5uCgPjD83vMq0beDL3T0QC41jZ_28747jGP1N1iN6QCecbvvzn3eWXaKO1M9RR3c-2PWRE7DazOcm-a9vY4toRRepXBi6IXFKYhaIgDTrV1vONYEhWidKFPwFjkUN2ABW7bqrNWcpXNpQ_Oszdx7G_JiCTH78O0i0W71Exc-S1QLIV-d-ZCj62VGybOTR0sG18HwCfj4yY3R-t8Q==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224bee000038feff2a_0%7C0a220b774bf200002286f566_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EcgFh32snNZLRxn03KziAzp6-1bJlWafHXqpDReDNxg3WN9X_JwVjgCksGu4UGz1HvFcTMoUlrX4OF2y00TZUT1qvto9zKpH8o1FnYulCYilf7K4mJ1OvToxMIY5UEC3kCbFs40jTyuUrMwDGYPhP-nav2JO_cb5EBxGVPndUwFBa3RFZWDMcG_tl0YDek3_RYKUS8PlU9JVR6ggyhtIOenZkVija-WcGz2U_Tmq3R9E91uYu-OIDpzjEEFnyhozTgl4UCa7zWUWFR1_9QcISO8eHeNjI42J9Rhn8PYgpvCmpxndKjXCuiz7BgJ1G7Aw7Npy5URjebp8Ed5EhTt8ASf2eqItr-YUe9eND11Pde2zx3uvG6bnXVQ4CvBuOJqecEfwURiSkvKL7bVBBkjTm9JEBVGqE8fpl_MAUkt1uGDVIJin1242k8QCLaTAfeMYV5av-lKenLzlzhytDI6SxxLN-rBPhmXM03JSOx_zjNLadix36SFwqaVowTyl76XBdsgs67_EWw_7vfOtMU_NBfOXEZ2Vw0ZamzFDoHeA7oOj6IXNyt-kOfcBqxuq3A0LvOc8-SM5uCgPjD83vMq0beDL3T0QC41jZ_28747jGP1N1iN6QCecbvvzn3eWXaKO1M9RR3c-2PWRE7DazOcm-a9vY4toRRepXBi6IXFKYhaIgDTrV1vONYEhWidKFPwFjkUN2ABW7bqrNWcpXNpQ_Oszdx7G_JiCTH78O0i0W71Exc-S1QLIV-d-ZCj62VGybOTR0sG18HwCfj4yY3R-t8Q==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-03-22T23:20:00.000Z", "utc_arrival": "2023-03-22T22:20:00.000Z", "local_departure": "2023-03-22T20:00:00.000Z", "utc_departure": "2023-03-22T19:00:00.000Z"}, {"id": "0b770a224c16000010748fcb_0|0a220b774c190000a5259c8e_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 678.100819, "distance": 1975.87, "duration": {"departure": 12600, "return": 11700, "total": 24300}, "price": 199446.0654, "conversion": {"EUR": 522.101209, "HUF": 199446.0654}, "fare": {"adults": 99723.03, "children": 99723.03, "infants": 99723.03}, "bags_price": {"1": 102.214, "2": 204.442}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 439, "hold_height": 149, "hold_length": 171, "hold_weight": 20, "hold_width": 119, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 2}, "airlines": ["W6"], "route": [{"id": "0b770a224c16000010748fcb_0", "combination_id": "0b770a224c16000010748fcb", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "JKREG", "fare_category": "M", "fare_classes": "J", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-01T19:45:00.000Z", "utc_arrival": "2023-05-01T17:45:00.000Z", "local_departure": "2023-05-01T16:15:00.000Z", "utc_departure": "2023-05-01T14:15:00.000Z"}, {"id": "0a220b774c190000a5259c8e_0", "combination_id": "0a220b774c190000a5259c8e", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IJREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-05T01:15:00.000Z", "utc_arrival": "2023-05-04T23:15:00.000Z", "local_departure": "2023-05-04T22:00:00.000Z", "utc_departure": "2023-05-04T20:00:00.000Z"}], "booking_token": "E5p9pLPHOhghX7kbyMe5r0mteuTUZVC8HeZpqZWSijQV3tPP2rrydAgCZGhnmkHE__AQ18WH3p6o8j2DtMt7NS07BDBnXrdVArCvaFsQZM5XkczMxpzZ0UOG_V84diPn9Ez80qQsBLr07zqKfxz8_CZdpj4o_NEAuLeL4YSmMFrPxoiGqU_XjqPnYJcwnidILpLsuXP3AXQqE4-Q6KxL_hdKK2t0sZ44EGLITxL6lHS5Rpgs4xqXvn8PRRaFs1nhCcVIPCuoUIjHOSJAV8FXynTHVUsDD723v3uSO0ZzyjUWqsWXHwn_WTSMaZ6CXXhXc0rio_lHHW46UQ95agdvFDJZ4gTAkU2JZu2v2BYby4e-4obvmOePRJbW4aKZcOyM-XF9HwPwSJdzeXXyBAyYvZ0r_Gr2H_InkBoutAnrTY670fCcuIy_jZ6lcZGIPXucgmkavDndciR9z7yPuVSf5jA9J2F3D9b3JEWL3J9tsNSV3WzDkVCBxg0cWBTIwLaIQxlchQIVqlFTmeCrpuIhNL-3Iiov-tRDk5onrWWJBM-2_GVjkb_iSTauNHf12QYSXF1vOfOfx-KZjp7gY9qYs3OSIfgnn18OGFgpWITTAfsLhVDv0Ru1luX3bJePfvgqEx6eEt-MEgrB-_JR2h7TCn3Gn_lLGWthDfIkOyUK6BmB3sDnoIco9zWd30nMCmP-RwtPElbhmHvDJYy-00oj5VjFpqKenYbzUBFIYPaMvrcfSQUa0qGxbjcm7SQ3-_0vHMYdfNg2HsQDl3ZopDdPJ2g==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c16000010748fcb_0%7C0a220b774c190000a5259c8e_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=E5p9pLPHOhghX7kbyMe5r0mteuTUZVC8HeZpqZWSijQV3tPP2rrydAgCZGhnmkHE__AQ18WH3p6o8j2DtMt7NS07BDBnXrdVArCvaFsQZM5XkczMxpzZ0UOG_V84diPn9Ez80qQsBLr07zqKfxz8_CZdpj4o_NEAuLeL4YSmMFrPxoiGqU_XjqPnYJcwnidILpLsuXP3AXQqE4-Q6KxL_hdKK2t0sZ44EGLITxL6lHS5Rpgs4xqXvn8PRRaFs1nhCcVIPCuoUIjHOSJAV8FXynTHVUsDD723v3uSO0ZzyjUWqsWXHwn_WTSMaZ6CXXhXc0rio_lHHW46UQ95agdvFDJZ4gTAkU2JZu2v2BYby4e-4obvmOePRJbW4aKZcOyM-XF9HwPwSJdzeXXyBAyYvZ0r_Gr2H_InkBoutAnrTY670fCcuIy_jZ6lcZGIPXucgmkavDndciR9z7yPuVSf5jA9J2F3D9b3JEWL3J9tsNSV3WzDkVCBxg0cWBTIwLaIQxlchQIVqlFTmeCrpuIhNL-3Iiov-tRDk5onrWWJBM-2_GVjkb_iSTauNHf12QYSXF1vOfOfx-KZjp7gY9qYs3OSIfgnn18OGFgpWITTAfsLhVDv0Ru1luX3bJePfvgqEx6eEt-MEgrB-_JR2h7TCn3Gn_lLGWthDfIkOyUK6BmB3sDnoIco9zWd30nMCmP-RwtPElbhmHvDJYy-00oj5VjFpqKenYbzUBFIYPaMvrcfSQUa0qGxbjcm7SQ3-_0vHMYdfNg2HsQDl3ZopDdPJ2g==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-01T19:45:00.000Z", "utc_arrival": "2023-05-01T17:45:00.000Z", "local_departure": "2023-05-01T16:15:00.000Z", "utc_departure": "2023-05-01T14:15:00.000Z"}, {"id": "0b770a224c3d000092cf2d05_0|0a220b774c400000ebc98d9f_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 677.746663, "distance": 1975.87, "duration": {"departure": 12000, "return": 11700, "total": 23700}, "price": 200329.457, "conversion": {"EUR": 524.413713, "HUF": 200329.457}, "fare": {"adults": 100164.73, "children": 100164.73, "infants": 100164.73}, "bags_price": {"1": 85.862, "2": 171.738}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 2}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224c3d000092cf2d05_0", "combination_id": "0b770a224c3d000092cf2d05", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-09T21:45:00.000Z", "utc_arrival": "2023-06-09T19:45:00.000Z", "local_departure": "2023-06-09T18:25:00.000Z", "utc_departure": "2023-06-09T16:25:00.000Z"}, {"id": "0a220b774c400000ebc98d9f_0", "combination_id": "0a220b774c400000ebc98d9f", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "JREG", "fare_category": "M", "fare_classes": "J", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-12T23:45:00.000Z", "utc_arrival": "2023-06-12T21:45:00.000Z", "local_departure": "2023-06-12T20:30:00.000Z", "utc_departure": "2023-06-12T18:30:00.000Z"}], "booking_token": "ErD5HM9XknfjGTKpfLLrT5d-ewdu1FxHU2S1QDTXREmW-tWtQCn8fxhMhRDJhYygVBOG7uGyaKZR7-AfgmLkRmeR0jE468ZA9uJ-lE9WHigMaysS0CglgQwmm8jUR-1qo3TyL5fWl6N1VIWcFl_QCBjSHNGCLWiltnd2Uh4EA79jMDF3k7eM1fyyUN9pveQUwPfSyqgbZQRRd8cGTBYg94g4y2DwIfXGhJpr_yX9EFh3zkVE61Twi9jf074bJVM-yUppUNJPsJW70kHMpguJA4Q9itbNnPCUYzEWVkwaLn6MbWYZCoXeuhdcZ7GcnK-25B3bDOopE52jS1Y_iR9W4tZAmlpE-DiNzX0hETqin8jJnam0QuDCxkDqHr-jWh1VhpPYhsBPyoJKJedZLRjyUGTX90bpl1FSqTuGQBV5G8UvWuc2XepFU4uRmSa_NntPma7Jm0v_1kIIatWCOU5rQx4JUqrV5fqy1tOmbvlB3hXH3zlnxVv7Ez4poko6_rJy9WUDlbh1APAgyX5SC4pNBPl1ipk337kP7zSjuWiJhyAaV2XCRDRCM4U0vI_Czki6P9bMTeAgAP4wxwXGJpPQGcLs0bEkTTKe03ec-iIUGjQwfx6qwjC4ekL698GP8BM2atOnNAvSHDftDdmyk1tKvDpVoPWeAOGza4kjUqe1ywZgJ9muEd1xKI9yImw1FGyuVh6Y7h-HmYhZ0Bg2d5L_E9Mcx7ylsXQFlmWGuRY9u6iwYLDrBJJApTD8pWT-_zEK_XaZvMSxBjnquyhLOGH3IeA==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c3d000092cf2d05_0%7C0a220b774c400000ebc98d9f_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=ErD5HM9XknfjGTKpfLLrT5d-ewdu1FxHU2S1QDTXREmW-tWtQCn8fxhMhRDJhYygVBOG7uGyaKZR7-AfgmLkRmeR0jE468ZA9uJ-lE9WHigMaysS0CglgQwmm8jUR-1qo3TyL5fWl6N1VIWcFl_QCBjSHNGCLWiltnd2Uh4EA79jMDF3k7eM1fyyUN9pveQUwPfSyqgbZQRRd8cGTBYg94g4y2DwIfXGhJpr_yX9EFh3zkVE61Twi9jf074bJVM-yUppUNJPsJW70kHMpguJA4Q9itbNnPCUYzEWVkwaLn6MbWYZCoXeuhdcZ7GcnK-25B3bDOopE52jS1Y_iR9W4tZAmlpE-DiNzX0hETqin8jJnam0QuDCxkDqHr-jWh1VhpPYhsBPyoJKJedZLRjyUGTX90bpl1FSqTuGQBV5G8UvWuc2XepFU4uRmSa_NntPma7Jm0v_1kIIatWCOU5rQx4JUqrV5fqy1tOmbvlB3hXH3zlnxVv7Ez4poko6_rJy9WUDlbh1APAgyX5SC4pNBPl1ipk337kP7zSjuWiJhyAaV2XCRDRCM4U0vI_Czki6P9bMTeAgAP4wxwXGJpPQGcLs0bEkTTKe03ec-iIUGjQwfx6qwjC4ekL698GP8BM2atOnNAvSHDftDdmyk1tKvDpVoPWeAOGza4kjUqe1ywZgJ9muEd1xKI9yImw1FGyuVh6Y7h-HmYhZ0Bg2d5L_E9Mcx7ylsXQFlmWGuRY9u6iwYLDrBJJApTD8pWT-_zEK_XaZvMSxBjnquyhLOGH3IeA==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-09T21:45:00.000Z", "utc_arrival": "2023-06-09T19:45:00.000Z", "local_departure": "2023-06-09T18:25:00.000Z", "utc_departure": "2023-06-09T16:25:00.000Z"}, {"id": "0b770a224c1d00001b98d770_0|0a220b774c21000064f4da0b_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 684.473948, "distance": 1975.87, "duration": {"departure": 12000, "return": 12900, "total": 24900}, "price": 200861.9607, "conversion": {"EUR": 525.807678, "HUF": 200861.9607}, "fare": {"adults": 100430.98, "children": 100430.98, "infants": 100430.98}, "bags_price": {"1": 85.12, "2": 170.24}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 2}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224c1d00001b98d770_0", "combination_id": "0b770a224c1d00001b98d770", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-08T14:00:00.000Z", "utc_arrival": "2023-05-08T12:00:00.000Z", "local_departure": "2023-05-08T10:40:00.000Z", "utc_departure": "2023-05-08T08:40:00.000Z"}, {"id": "0a220b774c21000064f4da0b_0", "combination_id": "0a220b774c21000064f4da0b", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "BOREG", "fare_category": "M", "fare_classes": "B", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-13T00:05:00.000Z", "utc_arrival": "2023-05-12T22:05:00.000Z", "local_departure": "2023-05-12T20:30:00.000Z", "utc_departure": "2023-05-12T18:30:00.000Z"}], "booking_token": "EqR3ILI7qZLNuVg7D96t56MNjIkL0l7VcaxikKmRCo5M9A8SzGIjgzpp3XL3tV_oC0LJ0dwn6fZ7Rojo4kqPVDSfGCrW8417_KvmS-XKzBd0ptBCAj9uqGNyKGdY3KoEd0TeZ4eWIkSdam-iXkIToqQorjo8k1aVqHJS0M5kFGWsO3I3svE7GvGkwGuuNukr_ZsOyBYCakpd9rpUBR5BPo_oxb_Kusr7eOWeANaH1eLn19dQAJVXsT4L-u81aBWFBChCRyHP79mrPwVeewT8g3YP34t5o1n8GXs1ubxhedqcfKG3dxuFyQrbNxfBZ_kobIvq752Op1luZoA6D_-ogAItKLyJyISoSlw--zKn_ChkWMcvLRZkp74qfDuu4irPBHIeW51eAo_-dUyLRLfHjTDMGaQaETYibTCGr5adwNI4HbqyRR7ZQR6MIrA-lPWBTPPSeE6Ghg7OHdqAaUo4Czwrm5SEZS7tqjllMWhrQ-k8oajPsGB70885I7THXBiISze9S159fATa94ITujDimitiY0Kzer8JbZCUAaO9YwIVdUcjuYOUvYFx315YqeZAnKwKWZ7nuvqzQ60Vt6aIIA0PEswr9BHqydy7dbqASCHhqqm-BlwjacYTDRuh1tGhKKeuMNqIO8Y7Yh6cv1xPoxsaziV3SJSc8kThkCbY8O3Ot4Tf7RTrgNICyHvOjDv0A_-1b8IO4HbA0GOZpXS8c21btEP8UwLvz8fPU-rfZcC2Y6WnH9BGJ2ly6yohqrUgnczr8VMIsVe9LzsXGvnjbXw==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c1d00001b98d770_0%7C0a220b774c21000064f4da0b_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EqR3ILI7qZLNuVg7D96t56MNjIkL0l7VcaxikKmRCo5M9A8SzGIjgzpp3XL3tV_oC0LJ0dwn6fZ7Rojo4kqPVDSfGCrW8417_KvmS-XKzBd0ptBCAj9uqGNyKGdY3KoEd0TeZ4eWIkSdam-iXkIToqQorjo8k1aVqHJS0M5kFGWsO3I3svE7GvGkwGuuNukr_ZsOyBYCakpd9rpUBR5BPo_oxb_Kusr7eOWeANaH1eLn19dQAJVXsT4L-u81aBWFBChCRyHP79mrPwVeewT8g3YP34t5o1n8GXs1ubxhedqcfKG3dxuFyQrbNxfBZ_kobIvq752Op1luZoA6D_-ogAItKLyJyISoSlw--zKn_ChkWMcvLRZkp74qfDuu4irPBHIeW51eAo_-dUyLRLfHjTDMGaQaETYibTCGr5adwNI4HbqyRR7ZQR6MIrA-lPWBTPPSeE6Ghg7OHdqAaUo4Czwrm5SEZS7tqjllMWhrQ-k8oajPsGB70885I7THXBiISze9S159fATa94ITujDimitiY0Kzer8JbZCUAaO9YwIVdUcjuYOUvYFx315YqeZAnKwKWZ7nuvqzQ60Vt6aIIA0PEswr9BHqydy7dbqASCHhqqm-BlwjacYTDRuh1tGhKKeuMNqIO8Y7Yh6cv1xPoxsaziV3SJSc8kThkCbY8O3Ot4Tf7RTrgNICyHvOjDv0A_-1b8IO4HbA0GOZpXS8c21btEP8UwLvz8fPU-rfZcC2Y6WnH9BGJ2ly6yohqrUgnczr8VMIsVe9LzsXGvnjbXw==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-08T14:00:00.000Z", "utc_arrival": "2023-05-08T12:00:00.000Z", "local_departure": "2023-05-08T10:40:00.000Z", "utc_departure": "2023-05-08T08:40:00.000Z"}, {"id": "0b770a224c470000e38f46b1_0|0a220b774c4b0000625e6e09_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 678.636712, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 201178.8023, "conversion": {"EUR": 526.637092, "HUF": 201178.8023}, "fare": {"adults": 100589.4, "children": 100589.4, "infants": 100589.4}, "bags_price": {"1": 76.706, "2": 163.212}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 158, "hold_height": 52, "hold_length": 78, "hold_weight": 20, "hold_width": 28, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 3, "personal_item_width": 15}, "availability": {"seats": 4}, "airlines": ["FR", "IB"], "route": [{"id": "0b770a224c470000e38f46b1_0", "combination_id": "0b770a224c470000e38f46b1", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-19T14:00:00.000Z", "utc_arrival": "2023-06-19T12:00:00.000Z", "local_departure": "2023-06-19T10:40:00.000Z", "utc_departure": "2023-06-19T08:40:00.000Z"}, {"id": "0a220b774c4b0000625e6e09_0", "combination_id": "0a220b774c4b0000625e6e09", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "IB", "flight_no": 3278, "operating_carrier": "IB", "operating_flight_no": "3278", "fare_basis": "QWNNAOB4", "fare_category": "M", "fare_classes": "Q", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-23T14:55:00.000Z", "utc_arrival": "2023-06-23T12:55:00.000Z", "local_departure": "2023-06-23T11:45:00.000Z", "utc_departure": "2023-06-23T09:45:00.000Z"}], "booking_token": "EXVEuWcOMXqI9oCgDbrDNIS-WzlFvld9CFRxwHHsqhC0EbN5GW0kRnk-pDUGS3rOnJnZ5bKV84Lv-Ac_-4SKHWv4r-TQAM388uTih7sTmI5LdEt3arnvSFIUF_pxcVAGFQiHJKUdAtf6zX4TVX1BSHGzk8HfgTuUGdT1snj2-OMBjjNG-j_UofNYzh8k6FBqr-Ahyt87KJYhWlEZgcF01OWSpMLYfRrHy_vDl8LVlMb9UIsY3iUaedlWH9v1fy8A9eAYyaYOZ3DhSXyXJ51K3BEeXzh_NSFGy2N1h98KR-w6bhfO71LrXnofrcymsV7lUz4t5DlnZIffoqfFU4Ff0xn3Ii7om_Rn3k9iJDSSLmgmKMpHIbwh3UaRopWOJr-laokSxovyM7a7WRmHsA-R4bji8I7R6C_Xj9LXpYHpDgntGh5GiUV3fEfPqOUPJc9hcsTcCTWonA3wdFowM3omLSOIqfInFVyx3fmXqmmm4fCT57IR_ZiOFTgzqjOZxkn33fVdXQLRp9FIdLVHl4ch0uSVSEtIl02_x3Z2iIcp-ws0H7DH_8nDHLEPvs7dTHHTpiuANgKmGzAZgBVweN3gyRJb1iyyxT02ZJuPV5orNiuh5Sph_DlgegYzLt8rHE86CMpgM6RNrXUn3w6Pov1bgMBOV4ZBFtS_Dx2D1coFW3zgWe_I2v8tJQSPrtTFpYLZ1fKXC3Q8KpXMvWn2N0jN45IuWcG2b1Et9d71l1tzxVBtTYPoi1cGuH_ecmy8xolRldsFzGOhyfEjUC6r8rcY6iHBUmYLjiwI5Hv-JGu_GQ30=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c470000e38f46b1_0%7C0a220b774c4b0000625e6e09_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EXVEuWcOMXqI9oCgDbrDNIS-WzlFvld9CFRxwHHsqhC0EbN5GW0kRnk-pDUGS3rOnJnZ5bKV84Lv-Ac_-4SKHWv4r-TQAM388uTih7sTmI5LdEt3arnvSFIUF_pxcVAGFQiHJKUdAtf6zX4TVX1BSHGzk8HfgTuUGdT1snj2-OMBjjNG-j_UofNYzh8k6FBqr-Ahyt87KJYhWlEZgcF01OWSpMLYfRrHy_vDl8LVlMb9UIsY3iUaedlWH9v1fy8A9eAYyaYOZ3DhSXyXJ51K3BEeXzh_NSFGy2N1h98KR-w6bhfO71LrXnofrcymsV7lUz4t5DlnZIffoqfFU4Ff0xn3Ii7om_Rn3k9iJDSSLmgmKMpHIbwh3UaRopWOJr-laokSxovyM7a7WRmHsA-R4bji8I7R6C_Xj9LXpYHpDgntGh5GiUV3fEfPqOUPJc9hcsTcCTWonA3wdFowM3omLSOIqfInFVyx3fmXqmmm4fCT57IR_ZiOFTgzqjOZxkn33fVdXQLRp9FIdLVHl4ch0uSVSEtIl02_x3Z2iIcp-ws0H7DH_8nDHLEPvs7dTHHTpiuANgKmGzAZgBVweN3gyRJb1iyyxT02ZJuPV5orNiuh5Sph_DlgegYzLt8rHE86CMpgM6RNrXUn3w6Pov1bgMBOV4ZBFtS_Dx2D1coFW3zgWe_I2v8tJQSPrtTFpYLZ1fKXC3Q8KpXMvWn2N0jN45IuWcG2b1Et9d71l1tzxVBtTYPoi1cGuH_ecmy8xolRldsFzGOhyfEjUC6r8rcY6iHBUmYLjiwI5Hv-JGu_GQ30=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-19T14:00:00.000Z", "utc_arrival": "2023-06-19T12:00:00.000Z", "local_departure": "2023-06-19T10:40:00.000Z", "utc_departure": "2023-06-19T08:40:00.000Z"}, {"id": "0b770a224c4800006d0d7298_0|0a220b774c4c00004355e863_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 680.135133, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 201751.2089, "conversion": {"EUR": 528.135513, "HUF": 201751.2089}, "fare": {"adults": 100875.6, "children": 100875.6, "infants": 100875.6}, "bags_price": {"1": 76.454, "2": 162.708}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 158, "hold_height": 52, "hold_length": 78, "hold_weight": 20, "hold_width": 28, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 3, "personal_item_width": 15}, "availability": {"seats": 3}, "airlines": ["FR", "VY"], "route": [{"id": "0b770a224c4800006d0d7298_0", "combination_id": "0b770a224c4800006d0d7298", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-20T10:15:00.000Z", "utc_arrival": "2023-06-20T08:15:00.000Z", "local_departure": "2023-06-20T06:55:00.000Z", "utc_departure": "2023-06-20T04:55:00.000Z"}, {"id": "0a220b774c4c00004355e863_0", "combination_id": "0a220b774c4c00004355e863", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "VY", "flight_no": 5192, "operating_carrier": "IB", "operating_flight_no": "3278", "fare_basis": "WNBBHJA", "fare_category": "M", "fare_classes": "W", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": "32S", "vehicle_type": "aircraft", "local_arrival": "2023-06-24T14:55:00.000Z", "utc_arrival": "2023-06-24T12:55:00.000Z", "local_departure": "2023-06-24T11:45:00.000Z", "utc_departure": "2023-06-24T09:45:00.000Z"}], "booking_token": "EMXSBEUnkQHn_6f7GKEBafiSE20K9I7wFXYr5vc21_Mzbfipod4tTlnWKT-dDuA97shFhfiFw8kw3lzZGAsKMY1CJbM1DfusRwYVTkk2sMGbzJ17fAGZoSHHVr6zUcxE0WxwYiL6oQOxKZgSdm0KIJ6W6NysX3vVTzTFL2C3Ql4A6Bw7B9oGREVQVzMb5C_LeYnMS_4i0eW4qzqT7vXoGXhkIIQM9jK_A0HV9nTgVjSjNJJHR3Ku8D-C8IJ6R6jmJM2weMUFTJqwZjybeTYkEXcwtt8ISVuNpXoYU3rSjvINdSkiDH4yxoifBmAQcE7A7V_hQXEqI-Sordmwm6h6qKz_2Evc_dj2a8mY5MNbPgtYWMeOMl1VLmLhSD0sy7VkYTnw2lR8KN1rVLYTaBcj0SRQyyAAO8oAGdAEIAeFln_GXZi0eYP5dzNYhurDSmPNXu6gtbTU3OO4YqLdTx1I07fM2d3kRsxqrDfrURH1aFJCFJA2gmd1ZpSIy5jmVltRSwMFj-z34kQSRpbz_O2_z0QRtiRlu6AtRC1BbRe34MiO2KwSDrjIltCBdPfgFsyz_XcVeSCsNgq_mkfcsKf_qFD1oBHCVhs79JHSJxHmQ4hQpXJge10WEwltnjDmf6XGjetJZ3YbgsJ4L2We4pY6I8WQv5F9N6PFkt-XBxcRJmtC8wN5RJeRCiO_bc4D7BAWBCQW_V0pDyyJ7jNHQtAtQ8YNjjJ9l-bLvnUbtosoBDp8cqPtLePfe7Sy3yyoRI0AG0kv85_rQyEWGWSI2uNuGoMmF4U7zj6c32b9KzwGUWTs=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c4800006d0d7298_0%7C0a220b774c4c00004355e863_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EMXSBEUnkQHn_6f7GKEBafiSE20K9I7wFXYr5vc21_Mzbfipod4tTlnWKT-dDuA97shFhfiFw8kw3lzZGAsKMY1CJbM1DfusRwYVTkk2sMGbzJ17fAGZoSHHVr6zUcxE0WxwYiL6oQOxKZgSdm0KIJ6W6NysX3vVTzTFL2C3Ql4A6Bw7B9oGREVQVzMb5C_LeYnMS_4i0eW4qzqT7vXoGXhkIIQM9jK_A0HV9nTgVjSjNJJHR3Ku8D-C8IJ6R6jmJM2weMUFTJqwZjybeTYkEXcwtt8ISVuNpXoYU3rSjvINdSkiDH4yxoifBmAQcE7A7V_hQXEqI-Sordmwm6h6qKz_2Evc_dj2a8mY5MNbPgtYWMeOMl1VLmLhSD0sy7VkYTnw2lR8KN1rVLYTaBcj0SRQyyAAO8oAGdAEIAeFln_GXZi0eYP5dzNYhurDSmPNXu6gtbTU3OO4YqLdTx1I07fM2d3kRsxqrDfrURH1aFJCFJA2gmd1ZpSIy5jmVltRSwMFj-z34kQSRpbz_O2_z0QRtiRlu6AtRC1BbRe34MiO2KwSDrjIltCBdPfgFsyz_XcVeSCsNgq_mkfcsKf_qFD1oBHCVhs79JHSJxHmQ4hQpXJge10WEwltnjDmf6XGjetJZ3YbgsJ4L2We4pY6I8WQv5F9N6PFkt-XBxcRJmtC8wN5RJeRCiO_bc4D7BAWBCQW_V0pDyyJ7jNHQtAtQ8YNjjJ9l-bLvnUbtosoBDp8cqPtLePfe7Sy3yyoRI0AG0kv85_rQyEWGWSI2uNuGoMmF4U7zj6c32b9KzwGUWTs=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-20T10:15:00.000Z", "utc_arrival": "2023-06-20T08:15:00.000Z", "local_departure": "2023-06-20T06:55:00.000Z", "utc_departure": "2023-06-20T04:55:00.000Z"}, {"id": "0b770a224bef0000f1a846fa_0|0a220b774bf200002286f566_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 682.07566, "distance": 1975.87, "duration": {"departure": 12000, "return": 11700, "total": 23700}, "price": 201983.1621, "conversion": {"EUR": 528.74271, "HUF": 201983.1621}, "fare": {"adults": 100991.58, "children": 100991.58, "infants": 100991.58}, "bags_price": {"1": 97.482, "2": 194.964}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 439, "hold_height": 149, "hold_length": 171, "hold_weight": 20, "hold_width": 119, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 3}, "airlines": ["W6"], "route": [{"id": "0b770a224bef0000f1a846fa_0", "combination_id": "0b770a224bef0000f1a846fa", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "KLREG", "fare_category": "M", "fare_classes": "K", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-03-23T19:40:00.000Z", "utc_arrival": "2023-03-23T18:40:00.000Z", "local_departure": "2023-03-23T16:20:00.000Z", "utc_departure": "2023-03-23T15:20:00.000Z"}, {"id": "0a220b774bf200002286f566_0", "combination_id": "0a220b774bf200002286f566", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IJREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-03-26T21:05:00.000Z", "utc_arrival": "2023-03-26T19:05:00.000Z", "local_departure": "2023-03-26T17:50:00.000Z", "utc_departure": "2023-03-26T15:50:00.000Z"}], "booking_token": "EQTmv1GKkUdwehtxONjmDLYj57K8YQ0U_5NAXOBEXf3_MkbjdJHbsBfpyjpgaVbYcySQ89efcg4g9iA78U31CLJecRypfTUOQ80S2LE_0JSXrfcTFSAnWEFPTo4LgXjikmzga6-jGa5hcPBPcehI6NEg4OrqGMyEP5dE3PL2O2kEwkFt7QPCmCbcMMZTze41xAdYGcqu5ha2qmr5OzBRVplviKtTdb68GvJ3CP_EZos6NEKUFE9dP-kU0PmT9n-a9P9aMK-cHgcSsfnnA26zNlnd9uNHKqgN5EMNzZ0nSko7IKlMjX_T21PCeNStRKoiqCgAcZcviBO5lF8KuSB7BMyUnVlz1docDE-h4R-Jh0AUfQaIK6ZpD6i1leCaLk8X8wGE3LnTSfp3epIIqbrbfmM3mrTQEEuBgZmRtKNvZ6QhbF3-XWprMY9Jfwd0Xy0fkIYhANq8vi7UqeqTbGsUOOnNQFkgilERxwcwZo_xoIpUE1EUGPZ4FPMyjR8De_4VBuwAc-RJUyZX55_cmVqsityx113B_kJ7utyYhnmjIWmC1kwDLfCnFXUG5UKCiaf3Kz4ux3xAagLLgX9SgWbc9cavvzt2ICOjrYeyAPJjyW2bT3E45o1LEfKAjTB6ry8T0Ke8brNO6dhg9J6fvMHe_oBmB51OPOrHQ5sstgreweMhNXrkiiBzdVmMwbtfcjn5YT3q6GpgvgfFnqxVsVUw1mlEn-vTuRmGbqf9-iUe314iIRSlS_vusYcbKgImy2hHFC3MMtpUgMwrx8Y3Avk5qIFmg5CezoAIF9eiDpRcYcfo=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224bef0000f1a846fa_0%7C0a220b774bf200002286f566_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EQTmv1GKkUdwehtxONjmDLYj57K8YQ0U_5NAXOBEXf3_MkbjdJHbsBfpyjpgaVbYcySQ89efcg4g9iA78U31CLJecRypfTUOQ80S2LE_0JSXrfcTFSAnWEFPTo4LgXjikmzga6-jGa5hcPBPcehI6NEg4OrqGMyEP5dE3PL2O2kEwkFt7QPCmCbcMMZTze41xAdYGcqu5ha2qmr5OzBRVplviKtTdb68GvJ3CP_EZos6NEKUFE9dP-kU0PmT9n-a9P9aMK-cHgcSsfnnA26zNlnd9uNHKqgN5EMNzZ0nSko7IKlMjX_T21PCeNStRKoiqCgAcZcviBO5lF8KuSB7BMyUnVlz1docDE-h4R-Jh0AUfQaIK6ZpD6i1leCaLk8X8wGE3LnTSfp3epIIqbrbfmM3mrTQEEuBgZmRtKNvZ6QhbF3-XWprMY9Jfwd0Xy0fkIYhANq8vi7UqeqTbGsUOOnNQFkgilERxwcwZo_xoIpUE1EUGPZ4FPMyjR8De_4VBuwAc-RJUyZX55_cmVqsityx113B_kJ7utyYhnmjIWmC1kwDLfCnFXUG5UKCiaf3Kz4ux3xAagLLgX9SgWbc9cavvzt2ICOjrYeyAPJjyW2bT3E45o1LEfKAjTB6ry8T0Ke8brNO6dhg9J6fvMHe_oBmB51OPOrHQ5sstgreweMhNXrkiiBzdVmMwbtfcjn5YT3q6GpgvgfFnqxVsVUw1mlEn-vTuRmGbqf9-iUe314iIRSlS_vusYcbKgImy2hHFC3MMtpUgMwrx8Y3Avk5qIFmg5CezoAIF9eiDpRcYcfo=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-03-23T19:40:00.000Z", "utc_arrival": "2023-03-23T18:40:00.000Z", "local_departure": "2023-03-23T16:20:00.000Z", "utc_departure": "2023-03-23T15:20:00.000Z"}, {"id": "0b770a224c15000010364d2a_0|0a220b774c190000a5259c8e_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 684.74232, "distance": 1975.87, "duration": {"departure": 12600, "return": 11700, "total": 24300}, "price": 201983.1621, "conversion": {"EUR": 528.74271, "HUF": 201983.1621}, "fare": {"adults": 100991.58, "children": 100991.58, "infants": 100991.58}, "bags_price": {"1": 106.624, "2": 213.234}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 439, "hold_height": 149, "hold_length": 171, "hold_weight": 20, "hold_width": 119, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 3}, "airlines": ["W6"], "route": [{"id": "0b770a224c15000010364d2a_0", "combination_id": "0b770a224c15000010364d2a", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "KLREG", "fare_category": "M", "fare_classes": "K", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-30T17:05:00.000Z", "utc_arrival": "2023-04-30T15:05:00.000Z", "local_departure": "2023-04-30T13:35:00.000Z", "utc_departure": "2023-04-30T11:35:00.000Z"}, {"id": "0a220b774c190000a5259c8e_0", "combination_id": "0a220b774c190000a5259c8e", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IJREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-05T01:15:00.000Z", "utc_arrival": "2023-05-04T23:15:00.000Z", "local_departure": "2023-05-04T22:00:00.000Z", "utc_departure": "2023-05-04T20:00:00.000Z"}], "booking_token": "EiK9pMcL9w4Zz8wBQFuSIK3_W8-If_nrnOhIrwN8X8EPpsXXd6PJ0I9jStDxNzUGGJw7CU-bAG57FDYxa9t6jtLyHG40_a7o_YQOVMYCP9vdIGjkd4fM7J8g0kkilIc-IVOqY41acKj8eSL3Atm3ImGqyHz_tRKI2I_ilnQI6b6ca_93JHBhdXdo2BxOwXlydQAOOXD3bf78g4qeLj8rqH470vWH_QlUh_njx4yAlXevjFSJ7Tbxifl-AaxROMYKu1z87n3pzTqHtjGh8-AgYpCR1QjxdPyav0PnQb-oEz9LSh1bGUzLYY7FpKU9iLsL_rGVp7B_gNz-26skdpyPNQ9hw6w5yOnC2ZYc9WBuqfw4X1PFYHY2_4WXkM40bC5KMyViUzrrVdYGesi6R1M33QR9Kb45_dqvnLVJ4FV0jJJ46aUfw59I9kV2cDtK40DSF0EmU6mo9Ap-8fXzW5U_vWIgqs5-uAqiYd2jC03vEcmmMOuMZY7v8IUB3hLAMC-lVtiPlZFW7INIamp6EZNBHKD-f1tHW9T_oftQgBlZe7ePs_Ap7q4Snd4NV_EZqB7-Z9A6ZrWxXThvXJ7I4xamdFXO8ZSsr1-JuZwndG-w8SyPs-9o058ESBSdMU0ce5yTvj3r92LKnIsqx6zb2swtx2RnO1mCqRio9IWnKblk8hrs6X7gxmXcI_cLgOqQE9b9-0rcrgciA_aYuQC-Vf558wbaj2g1XR-QjQ3-b3-LnvTrt79P-EevL5owiT2VaFwNnKUuvOxmyqozOSRmgXyxKbjD4LPTmx9pPuLaLwgSUzX4=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c15000010364d2a_0%7C0a220b774c190000a5259c8e_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EiK9pMcL9w4Zz8wBQFuSIK3_W8-If_nrnOhIrwN8X8EPpsXXd6PJ0I9jStDxNzUGGJw7CU-bAG57FDYxa9t6jtLyHG40_a7o_YQOVMYCP9vdIGjkd4fM7J8g0kkilIc-IVOqY41acKj8eSL3Atm3ImGqyHz_tRKI2I_ilnQI6b6ca_93JHBhdXdo2BxOwXlydQAOOXD3bf78g4qeLj8rqH470vWH_QlUh_njx4yAlXevjFSJ7Tbxifl-AaxROMYKu1z87n3pzTqHtjGh8-AgYpCR1QjxdPyav0PnQb-oEz9LSh1bGUzLYY7FpKU9iLsL_rGVp7B_gNz-26skdpyPNQ9hw6w5yOnC2ZYc9WBuqfw4X1PFYHY2_4WXkM40bC5KMyViUzrrVdYGesi6R1M33QR9Kb45_dqvnLVJ4FV0jJJ46aUfw59I9kV2cDtK40DSF0EmU6mo9Ap-8fXzW5U_vWIgqs5-uAqiYd2jC03vEcmmMOuMZY7v8IUB3hLAMC-lVtiPlZFW7INIamp6EZNBHKD-f1tHW9T_oftQgBlZe7ePs_Ap7q4Snd4NV_EZqB7-Z9A6ZrWxXThvXJ7I4xamdFXO8ZSsr1-JuZwndG-w8SyPs-9o058ESBSdMU0ce5yTvj3r92LKnIsqx6zb2swtx2RnO1mCqRio9IWnKblk8hrs6X7gxmXcI_cLgOqQE9b9-0rcrgciA_aYuQC-Vf558wbaj2g1XR-QjQ3-b3-LnvTrt79P-EevL5owiT2VaFwNnKUuvOxmyqozOSRmgXyxKbjD4LPTmx9pPuLaLwgSUzX4=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-04-30T17:05:00.000Z", "utc_arrival": "2023-04-30T15:05:00.000Z", "local_departure": "2023-04-30T13:35:00.000Z", "utc_departure": "2023-04-30T11:35:00.000Z"}, {"id": "0b770a224c3e0000d8f9b259_0|0a220b774c4200006eb2e849_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 682.014884, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 202469.286, "conversion": {"EUR": 530.015264, "HUF": 202469.286}, "fare": {"adults": 101234.64, "children": 101234.64, "infants": 101234.64}, "bags_price": {"1": 76.706, "2": 163.212}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 158, "hold_height": 52, "hold_length": 78, "hold_weight": 20, "hold_width": 28, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 3, "personal_item_width": 15}, "availability": {"seats": 6}, "airlines": ["FR", "IB"], "route": [{"id": "0b770a224c3e0000d8f9b259_0", "combination_id": "0b770a224c3e0000d8f9b259", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-10T13:25:00.000Z", "utc_arrival": "2023-06-10T11:25:00.000Z", "local_departure": "2023-06-10T10:05:00.000Z", "utc_departure": "2023-06-10T08:05:00.000Z"}, {"id": "0a220b774c4200006eb2e849_0", "combination_id": "0a220b774c4200006eb2e849", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "IB", "flight_no": 3278, "operating_carrier": "IB", "operating_flight_no": "3278", "fare_basis": "NZNNAOB4", "fare_category": "M", "fare_classes": "N", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-14T14:55:00.000Z", "utc_arrival": "2023-06-14T12:55:00.000Z", "local_departure": "2023-06-14T11:45:00.000Z", "utc_departure": "2023-06-14T09:45:00.000Z"}], "booking_token": "EmJD1yX1vP2rd1QbZXndtaFBMNebmLqWjoZ50SdKmONBAsChLllyBvFMbtdh3dJvFolbBbmE-GT6ZCRJfRjA37d_7lvvN-gwP0ncgkPRj1HBSFy34jzBGcSLb8G569cxgnKPn5pVcgfErmEXR75G8hJNBBvn5FDzOF9wgVY0DXEU02ERsECBWYg77xP4Rt1WsUI1MjoFWSduMCLNgFQMDE6rQNy-OkrpsNe1Wi5X-VDrP6AH-sIVzS0ShUH0uWbuLxM4ApNfgzr3nWJKXW8bUONC76JnznccMvhdMgTNBZ_HhTx9_yZm452ah8fEhMpmtFE4ZL8L_F7EYZ1HCu1kXsOQ1s3NhJZe-7XUxYvuWM2YzMYWV81L-eJ3KOFfgcK9TBtS84NLcOMuXwoaBnpX5TbwopIez7jSeq6ICJ_fJKkVqkJ6MvMRkLZiOF-zWFchyO6TRQX2IKiWEHh7y6rMjf9P3XPrlrBsUartZWWDM16QkLP0Qw4bws-NBj7aYDrJ1ZecJtdjv0-t3tJqjCnPWdwiAuEJMKpj4agC9iFOqOHkSsPuD2YfyaWrJjfSOPgLI-dbjMgncKhqSI0rlRBxtAvMeRc2R1mZ0ZkCdsyyao-jhfZlx3XV0mPVixpxskmZgFTpEifUktc3I5pqrxNaEiJfXCahoAhtJpIubdmb3lli4l72tZ5xmMcFpjMO-b29PAGxMnfJirM-JNA9NSrwvROrdpw0b9tbr0ZFQEq--sUr-Saz6yow1_wsViOzg2aQA", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c3e0000d8f9b259_0%7C0a220b774c4200006eb2e849_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EmJD1yX1vP2rd1QbZXndtaFBMNebmLqWjoZ50SdKmONBAsChLllyBvFMbtdh3dJvFolbBbmE-GT6ZCRJfRjA37d_7lvvN-gwP0ncgkPRj1HBSFy34jzBGcSLb8G569cxgnKPn5pVcgfErmEXR75G8hJNBBvn5FDzOF9wgVY0DXEU02ERsECBWYg77xP4Rt1WsUI1MjoFWSduMCLNgFQMDE6rQNy-OkrpsNe1Wi5X-VDrP6AH-sIVzS0ShUH0uWbuLxM4ApNfgzr3nWJKXW8bUONC76JnznccMvhdMgTNBZ_HhTx9_yZm452ah8fEhMpmtFE4ZL8L_F7EYZ1HCu1kXsOQ1s3NhJZe-7XUxYvuWM2YzMYWV81L-eJ3KOFfgcK9TBtS84NLcOMuXwoaBnpX5TbwopIez7jSeq6ICJ_fJKkVqkJ6MvMRkLZiOF-zWFchyO6TRQX2IKiWEHh7y6rMjf9P3XPrlrBsUartZWWDM16QkLP0Qw4bws-NBj7aYDrJ1ZecJtdjv0-t3tJqjCnPWdwiAuEJMKpj4agC9iFOqOHkSsPuD2YfyaWrJjfSOPgLI-dbjMgncKhqSI0rlRBxtAvMeRc2R1mZ0ZkCdsyyao-jhfZlx3XV0mPVixpxskmZgFTpEifUktc3I5pqrxNaEiJfXCahoAhtJpIubdmb3lli4l72tZ5xmMcFpjMO-b29PAGxMnfJirM-JNA9NSrwvROrdpw0b9tbr0ZFQEq--sUr-Saz6yow1_wsViOzg2aQA", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-10T13:25:00.000Z", "utc_arrival": "2023-06-10T11:25:00.000Z", "local_departure": "2023-06-10T10:05:00.000Z", "utc_departure": "2023-06-10T08:05:00.000Z"}, {"id": "0b770a224bef0000e50ad4c9_0|0a220b774bf3000020faa1b2_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 686.733015, "distance": 1975.87, "duration": {"departure": 12000, "return": 11700, "total": 23700}, "price": 203762.3021, "conversion": {"EUR": 533.400065, "HUF": 203762.3021}, "fare": {"adults": 101881.15, "children": 101881.15, "infants": 101881.15}, "bags_price": {"1": 77.014, "2": 154.028}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 2}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224bef0000e50ad4c9_0", "combination_id": "0b770a224bef0000e50ad4c9", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-03-23T13:40:00.000Z", "utc_arrival": "2023-03-23T12:40:00.000Z", "local_departure": "2023-03-23T10:20:00.000Z", "utc_departure": "2023-03-23T09:20:00.000Z"}, {"id": "0a220b774bf3000020faa1b2_0", "combination_id": "0a220b774bf3000020faa1b2", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IJREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-03-27T23:45:00.000Z", "utc_arrival": "2023-03-27T21:45:00.000Z", "local_departure": "2023-03-27T20:30:00.000Z", "utc_departure": "2023-03-27T18:30:00.000Z"}], "booking_token": "EiyfV9qSPfDzzXWR6IfUlop12D0YAMNSo2WCpwo7QbrGfUUV22NAP5XdOY2P7-TUnOkZyXy80kcZxlM5OsW2nRiCN5dssj1gnp9aVhPzrszgbkl4L2Je_qGzVlPAuLrPaDGmeX3ObyJwnNcnZrLxL-QwycwymLEi40D3GNWcoz45t_bfpiRHbS0Y5BsWMdHqWRMU61Ho4FnouQWw0O519xYFnt9C16U3CLeFSQMBiLo0BmDhUMfnRiMbQWzHLsAUymgGfLDSt2M7NdXaMBnM2ZIeNjZhrfKm84N0PitXv4u2IVzlCW3ai9usZRxHP32vUk6mfCjcDHu2H8DJjaTymuTQ_-0--nv4iw7cGA3De5aCGxvdr8lEE1xCwhGGkYYNx4gHPRw8EhfDLuzA_9pqBDhYYj0071auSmFiw5GBZ02brGN6hF8jD0mtr9dFgA_EpjU2U5PrjwY5wERBecyYrqGKId5z4sTBhbIYwrnARqqPFy5TYNcqvg2KQ7ENmz4AHBYvpVLNOI4shGkiptFaCmz2Ou-bhH04QK6I7XteqzfkKMugqHAWs8jiEU6fK3tookXyzbnByI7G38vyLGtw1JYaOeGGqU_Fz1HLsyZSatxRELVbXsf9HOwRGRDlG2hmfEYgkK6TaddocrepGZD0deqDO0BPgOTgggt6FNrnWzyjvWCa2Wjr3KIQSraYbVDmboHqmC9_SpxMPdoKiM_iiRg9W-HbJA8oUrjHARXc0eQ_j0x9ZtiKuQ_uHiMObE2B1HL0KubvAPYELzgD2a0Vi8w==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224bef0000e50ad4c9_0%7C0a220b774bf3000020faa1b2_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EiyfV9qSPfDzzXWR6IfUlop12D0YAMNSo2WCpwo7QbrGfUUV22NAP5XdOY2P7-TUnOkZyXy80kcZxlM5OsW2nRiCN5dssj1gnp9aVhPzrszgbkl4L2Je_qGzVlPAuLrPaDGmeX3ObyJwnNcnZrLxL-QwycwymLEi40D3GNWcoz45t_bfpiRHbS0Y5BsWMdHqWRMU61Ho4FnouQWw0O519xYFnt9C16U3CLeFSQMBiLo0BmDhUMfnRiMbQWzHLsAUymgGfLDSt2M7NdXaMBnM2ZIeNjZhrfKm84N0PitXv4u2IVzlCW3ai9usZRxHP32vUk6mfCjcDHu2H8DJjaTymuTQ_-0--nv4iw7cGA3De5aCGxvdr8lEE1xCwhGGkYYNx4gHPRw8EhfDLuzA_9pqBDhYYj0071auSmFiw5GBZ02brGN6hF8jD0mtr9dFgA_EpjU2U5PrjwY5wERBecyYrqGKId5z4sTBhbIYwrnARqqPFy5TYNcqvg2KQ7ENmz4AHBYvpVLNOI4shGkiptFaCmz2Ou-bhH04QK6I7XteqzfkKMugqHAWs8jiEU6fK3tookXyzbnByI7G38vyLGtw1JYaOeGGqU_Fz1HLsyZSatxRELVbXsf9HOwRGRDlG2hmfEYgkK6TaddocrepGZD0deqDO0BPgOTgggt6FNrnWzyjvWCa2Wjr3KIQSraYbVDmboHqmC9_SpxMPdoKiM_iiRg9W-HbJA8oUrjHARXc0eQ_j0x9ZtiKuQ_uHiMObE2B1HL0KubvAPYELzgD2a0Vi8w==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-03-23T13:40:00.000Z", "utc_arrival": "2023-03-23T12:40:00.000Z", "local_departure": "2023-03-23T10:20:00.000Z", "utc_departure": "2023-03-23T09:20:00.000Z"}, {"id": "0b770a224bfb0000cba453bb_0|0a220b774bff0000c1283ea2_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 686.607409, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 204223.6605, "conversion": {"EUR": 534.607789, "HUF": 204223.6605}, "fare": {"adults": 102111.83, "children": 102111.83, "infants": 102111.83}, "bags_price": {"1": 100.604, "2": 211.022}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 158, "hold_height": 52, "hold_length": 78, "hold_weight": 20, "hold_width": 28, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 3, "personal_item_width": 15}, "availability": {"seats": 2}, "airlines": ["FR", "IB"], "route": [{"id": "0b770a224bfb0000cba453bb_0", "combination_id": "0b770a224bfb0000cba453bb", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-04T10:15:00.000Z", "utc_arrival": "2023-04-04T08:15:00.000Z", "local_departure": "2023-04-04T06:55:00.000Z", "utc_departure": "2023-04-04T04:55:00.000Z"}, {"id": "0a220b774bff0000c1283ea2_0", "combination_id": "0a220b774bff0000c1283ea2", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "IB", "flight_no": 3278, "operating_carrier": "IB", "operating_flight_no": "3278", "fare_basis": "ADNNAOB4", "fare_category": "M", "fare_classes": "A", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-08T14:55:00.000Z", "utc_arrival": "2023-04-08T12:55:00.000Z", "local_departure": "2023-04-08T11:45:00.000Z", "utc_departure": "2023-04-08T09:45:00.000Z"}], "booking_token": "ETZUuvcaR3kAU72S_GD0lNUp8PYfkhj06UlykEC8Jrq5nSNk3naQzaGBwyb-WN4d3L81hgLlJ8IMqwk2_aDK7Gbt1jm3MtX5GBc2TrV_w3Yv0v9_ABp3XKUL2Q9afJ_N6XvdzFSODwfPf4DFVwblTvenJd3hJW4vBLMFJzoTl7pxd5Lje9cOWOrfS_KFul1hEPKDP7xwAOfFK7b-O2wEk1iCunOOwbtkihVgRvJiLZf9OOeQ-KzTn6besbs5at3fhXOpDR-SPwRg5D15fHM4OJP5IGGmNsG-xfZwCDBbc5XG6oxQkCMrm9JV0bCASRR4PiJGW74EUYzmxFKcsggOgAseKm-x2y8-jSQLvs9I59TPiCC3EEptDCbUpNB3qtkm_7jlYIt_EK6Em9LeQ4-CqqzOygYayQZov7mQAqV52WVGDJJx8iUQ-JW45tXuMxrQ7omVA_IhHBcaSK89oSM2J8lKeo_5wkdjsJPVmKSjUPQzbZb8i0KGzI-DpsjwPsmstniuKapZezfHglbnTSiGF8UhY8XGsUlHnIR8U0jdgI3sbcX7OCiwwxCyVGZ9NPSTiZVC2XIXfplxMN5j8dmEJCfMLSgACzO8A4u3Gq0MabuDSsf8iJ2LBW7pWhDFqpUBGURCB1GyOEyqg-QDuqJCmXl3SY4p-snH0mTOn85YkM0Opjn6Kn7QaOOdv7h7ltAtyR_xW7WxtGWEh0UW_C1LPKLxlk4Xbwvf8oUgC7KL1iGzlh-sdsTOLZfoDLBpA2NQDmbLXtNtbSE9N2NYhNXbTQFzTFLxeSxbSkklLvXZ9xzQ=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224bfb0000cba453bb_0%7C0a220b774bff0000c1283ea2_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=ETZUuvcaR3kAU72S_GD0lNUp8PYfkhj06UlykEC8Jrq5nSNk3naQzaGBwyb-WN4d3L81hgLlJ8IMqwk2_aDK7Gbt1jm3MtX5GBc2TrV_w3Yv0v9_ABp3XKUL2Q9afJ_N6XvdzFSODwfPf4DFVwblTvenJd3hJW4vBLMFJzoTl7pxd5Lje9cOWOrfS_KFul1hEPKDP7xwAOfFK7b-O2wEk1iCunOOwbtkihVgRvJiLZf9OOeQ-KzTn6besbs5at3fhXOpDR-SPwRg5D15fHM4OJP5IGGmNsG-xfZwCDBbc5XG6oxQkCMrm9JV0bCASRR4PiJGW74EUYzmxFKcsggOgAseKm-x2y8-jSQLvs9I59TPiCC3EEptDCbUpNB3qtkm_7jlYIt_EK6Em9LeQ4-CqqzOygYayQZov7mQAqV52WVGDJJx8iUQ-JW45tXuMxrQ7omVA_IhHBcaSK89oSM2J8lKeo_5wkdjsJPVmKSjUPQzbZb8i0KGzI-DpsjwPsmstniuKapZezfHglbnTSiGF8UhY8XGsUlHnIR8U0jdgI3sbcX7OCiwwxCyVGZ9NPSTiZVC2XIXfplxMN5j8dmEJCfMLSgACzO8A4u3Gq0MabuDSsf8iJ2LBW7pWhDFqpUBGURCB1GyOEyqg-QDuqJCmXl3SY4p-snH0mTOn85YkM0Opjn6Kn7QaOOdv7h7ltAtyR_xW7WxtGWEh0UW_C1LPKLxlk4Xbwvf8oUgC7KL1iGzlh-sdsTOLZfoDLBpA2NQDmbLXtNtbSE9N2NYhNXbTQFzTFLxeSxbSkklLvXZ9xzQ=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-04-04T10:15:00.000Z", "utc_arrival": "2023-04-04T08:15:00.000Z", "local_departure": "2023-04-04T06:55:00.000Z", "utc_departure": "2023-04-04T04:55:00.000Z"}, {"id": "0b770a224c36000074fbf6e5_0|0a220b774c390000ac91a717_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 689.301953, "distance": 1975.87, "duration": {"departure": 12600, "return": 11400, "total": 24000}, "price": 204234.3124, "conversion": {"EUR": 534.635673, "HUF": 204234.3124}, "fare": {"adults": 102117.16, "children": 102117.16, "infants": 102117.16}, "bags_price": {"1": 93.744, "2": 187.488}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 2}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224c36000074fbf6e5_0", "combination_id": "0b770a224c36000074fbf6e5", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-02T19:45:00.000Z", "utc_arrival": "2023-06-02T17:45:00.000Z", "local_departure": "2023-06-02T16:15:00.000Z", "utc_departure": "2023-06-02T14:15:00.000Z"}, {"id": "0a220b774c390000ac91a717_0", "combination_id": "0a220b774c390000ac91a717", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-05T10:15:00.000Z", "utc_arrival": "2023-06-05T08:15:00.000Z", "local_departure": "2023-06-05T07:05:00.000Z", "utc_departure": "2023-06-05T05:05:00.000Z"}], "booking_token": "E1QBZxU6uZ2VuroYITc0HQSSNf74YE3aC2A4hvpBr21rCfiCvX0tfiEi7h9oyOxkyftx3YkUEojegmErWuCg4I9Zr5D-Ep_5xmg2Zg4Fk82ge5mZVjMG1epo4rn9NOzf8sQ-uMTBVr9znmF9wrCRIP25LfXT7sHyXlv2m2VvxL6myJE4dTZ8UMxWyvI5dZakLSMpMCktDPXrdXGGjyCx4cVmjWYT3HG6v2eoESHLnqxXN8C2ACDfMn-f2otZC7qSMGGL6irBTr2K50GPHLkUj0PSODv_gkhPJzIjsAB-Gj9hFMaeJU6xs9AK2MEUmQk5Rx1DiiyGQDY00P7B4-ZIEqwXqeh9IW7j2fVZfpJVA0bo2sc-QsySJJweZBKeUoWL4XV-xdmvvkw06_auzwpcVe0ccDoWDU0-uxPxOmiPuhOnRXwiGyjUMUMhmRF8tvlWAAFegwux2KbWr7SHuhtZyVgIPP9OUH7NmAhQS6JfbTPt7IsDcrCjJGDPks_ydjs2vwOO0HK0g6p-Kqzg_Q6AOxJKGnprEBIS6oCgVj-ftbWknMrutQW_bqO_DwyumDkEXysNr1eAoWpq5ZRpEQPXO16Wx-Rl9r2by2rCG7i3ZbRATKLzcTzCwTHV0QwNhRARZe8yW7WusNSECEJFGZ1UMB1-15mAwHkuZZUG62g0vU3zQFi04AEvTqTc3RQGaokEgusdT_kGAwDcbdzOGmTf01Cl0q2T-uszYON9UgzbTQye57NLEwi-HKxSz50XDmTlvhqiULB92CU5ZqlhUXXoIdw==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c36000074fbf6e5_0%7C0a220b774c390000ac91a717_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=E1QBZxU6uZ2VuroYITc0HQSSNf74YE3aC2A4hvpBr21rCfiCvX0tfiEi7h9oyOxkyftx3YkUEojegmErWuCg4I9Zr5D-Ep_5xmg2Zg4Fk82ge5mZVjMG1epo4rn9NOzf8sQ-uMTBVr9znmF9wrCRIP25LfXT7sHyXlv2m2VvxL6myJE4dTZ8UMxWyvI5dZakLSMpMCktDPXrdXGGjyCx4cVmjWYT3HG6v2eoESHLnqxXN8C2ACDfMn-f2otZC7qSMGGL6irBTr2K50GPHLkUj0PSODv_gkhPJzIjsAB-Gj9hFMaeJU6xs9AK2MEUmQk5Rx1DiiyGQDY00P7B4-ZIEqwXqeh9IW7j2fVZfpJVA0bo2sc-QsySJJweZBKeUoWL4XV-xdmvvkw06_auzwpcVe0ccDoWDU0-uxPxOmiPuhOnRXwiGyjUMUMhmRF8tvlWAAFegwux2KbWr7SHuhtZyVgIPP9OUH7NmAhQS6JfbTPt7IsDcrCjJGDPks_ydjs2vwOO0HK0g6p-Kqzg_Q6AOxJKGnprEBIS6oCgVj-ftbWknMrutQW_bqO_DwyumDkEXysNr1eAoWpq5ZRpEQPXO16Wx-Rl9r2by2rCG7i3ZbRATKLzcTzCwTHV0QwNhRARZe8yW7WusNSECEJFGZ1UMB1-15mAwHkuZZUG62g0vU3zQFi04AEvTqTc3RQGaokEgusdT_kGAwDcbdzOGmTf01Cl0q2T-uszYON9UgzbTQye57NLEwi-HKxSz50XDmTlvhqiULB92CU5ZqlhUXXoIdw==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-02T19:45:00.000Z", "utc_arrival": "2023-06-02T17:45:00.000Z", "local_departure": "2023-06-02T16:15:00.000Z", "utc_departure": "2023-06-02T14:15:00.000Z"}, {"id": "0b770a224c43000004103d82_0|0a220b774c46000040adc89d_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 687.04435, "distance": 1975.87, "duration": {"departure": 11700, "return": 11700, "total": 23400}, "price": 204390.5748, "conversion": {"EUR": 535.04473, "HUF": 204390.5748}, "fare": {"adults": 102195.29, "children": 102195.29, "infants": 102195.29}, "bags_price": {"1": 97.118, "2": 204.036}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 158, "hold_height": 52, "hold_length": 78, "hold_weight": 20, "hold_width": 28, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 3, "personal_item_width": 15}, "availability": {"seats": 2}, "airlines": ["W6", "IB"], "route": [{"id": "0b770a224c43000004103d82_0", "combination_id": "0b770a224c43000004103d82", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "IB", "flight_no": 3279, "operating_carrier": "IB", "operating_flight_no": "3279", "fare_basis": "ADNNAOB4", "fare_category": "M", "fare_classes": "A", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-15T18:50:00.000Z", "utc_arrival": "2023-06-15T16:50:00.000Z", "local_departure": "2023-06-15T15:35:00.000Z", "utc_departure": "2023-06-15T13:35:00.000Z"}, {"id": "0a220b774c46000040adc89d_0", "combination_id": "0a220b774c46000040adc89d", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "JREG", "fare_category": "M", "fare_classes": "J", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-18T21:05:00.000Z", "utc_arrival": "2023-06-18T19:05:00.000Z", "local_departure": "2023-06-18T17:50:00.000Z", "utc_departure": "2023-06-18T15:50:00.000Z"}], "booking_token": "EyplDQzZ0H-iPCuB1n44_aJ27SR9smJfho1Q4w2484Ggrsnsw1iZ1Kc3a4OXjneyy74fFJtrfaBdD2xBCDxw6eb1GxTxJhAk-c0xOt28mbR6m8IXA89eUU658EU3NRM0s2WAMBbn0APr47hU5ApCo2n3RiYjOPvyTjhzyMWWOiH1C-ggsPEQZYMb6L__SBtTeJY0IhEor3z2hoiZRXenNVLWeyQYQYlAY0GZmR27VMWnaLMpk2V_Oa5cQDqbMWgLeHGdl7hiTAASoSN276uBFMNc_9Ucdzc8m8ML9xCsULrpxU9r5ktKbq3SYhajiP6pLnEG5XYS1utCBqK1TekDhrOFfhJB6LXyp6Usn4OaSOYZ-zZxYb8n--_pWvc39gRr9N6bvADAkDzyD_mZOiF4q84_J6gqhvQy8wPpFoJ9crnZfyo-x09SwCyT0qyg9gUG25tsJrDJDgY9mTIaxkRJmaccr2rZaQjXTZaqMY-GiShffesO0lJAeMtqQxwnq-XoZWd4za8bYn1PhUDNMhxb_RxhvdezTDOZDdKhtmsKdoOAisoAMqcTppiCqDXXLqnA4Sg4LRp8EU0xMInKriebvUngc2-VPc23Hi0vJhADXvYIXdOA3VYoFsbx_2q_TfEP-aYnc3htq_qjsyImCwCCJV01lSkrBuJqBNAOrz0ROt11AMtJzeV8KBGwft-ZXZo9y9kbn-b7iqIZG1NTpukd5LqptUqHd-fuBILRJ9gSbe-4Zji4v13lEYEeCT0y4WviYQVTgGV-fK2kuB_gjLv1D5TH74I6rqQ9_o32d7ZRxwh6vtiP7QdJp0OMhKnQz87_F", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c43000004103d82_0%7C0a220b774c46000040adc89d_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EyplDQzZ0H-iPCuB1n44_aJ27SR9smJfho1Q4w2484Ggrsnsw1iZ1Kc3a4OXjneyy74fFJtrfaBdD2xBCDxw6eb1GxTxJhAk-c0xOt28mbR6m8IXA89eUU658EU3NRM0s2WAMBbn0APr47hU5ApCo2n3RiYjOPvyTjhzyMWWOiH1C-ggsPEQZYMb6L__SBtTeJY0IhEor3z2hoiZRXenNVLWeyQYQYlAY0GZmR27VMWnaLMpk2V_Oa5cQDqbMWgLeHGdl7hiTAASoSN276uBFMNc_9Ucdzc8m8ML9xCsULrpxU9r5ktKbq3SYhajiP6pLnEG5XYS1utCBqK1TekDhrOFfhJB6LXyp6Usn4OaSOYZ-zZxYb8n--_pWvc39gRr9N6bvADAkDzyD_mZOiF4q84_J6gqhvQy8wPpFoJ9crnZfyo-x09SwCyT0qyg9gUG25tsJrDJDgY9mTIaxkRJmaccr2rZaQjXTZaqMY-GiShffesO0lJAeMtqQxwnq-XoZWd4za8bYn1PhUDNMhxb_RxhvdezTDOZDdKhtmsKdoOAisoAMqcTppiCqDXXLqnA4Sg4LRp8EU0xMInKriebvUngc2-VPc23Hi0vJhADXvYIXdOA3VYoFsbx_2q_TfEP-aYnc3htq_qjsyImCwCCJV01lSkrBuJqBNAOrz0ROt11AMtJzeV8KBGwft-ZXZo9y9kbn-b7iqIZG1NTpukd5LqptUqHd-fuBILRJ9gSbe-4Zji4v13lEYEeCT0y4WviYQVTgGV-fK2kuB_gjLv1D5TH74I6rqQ9_o32d7ZRxwh6vtiP7QdJp0OMhKnQz87_F", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-15T18:50:00.000Z", "utc_arrival": "2023-06-15T16:50:00.000Z", "local_departure": "2023-06-15T15:35:00.000Z", "utc_departure": "2023-06-15T13:35:00.000Z"}, {"id": "0b770a224c4400001cdf0063_0|0a220b774c4800001d928f51_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 690.284967, "distance": 1975.87, "duration": {"departure": 12600, "return": 11400, "total": 24000}, "price": 204609.8301, "conversion": {"EUR": 535.618687, "HUF": 204609.8301}, "fare": {"adults": 102304.92, "children": 108659.69, "infants": 108659.69}, "bags_price": {"1": 75.054, "2": 157.122}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 7}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224c4400001cdf0063_0", "combination_id": "0b770a224c4400001cdf0063", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "HIREG", "fare_category": "M", "fare_classes": "H", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-16T19:45:00.000Z", "utc_arrival": "2023-06-16T17:45:00.000Z", "local_departure": "2023-06-16T16:15:00.000Z", "utc_departure": "2023-06-16T14:15:00.000Z"}, {"id": "0a220b774c4800001d928f51_0", "combination_id": "0a220b774c4800001d928f51", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-20T14:05:00.000Z", "utc_arrival": "2023-06-20T12:05:00.000Z", "local_departure": "2023-06-20T10:55:00.000Z", "utc_departure": "2023-06-20T08:55:00.000Z"}], "booking_token": "E7qbKvVLmYLb2DSc8KAEfk3FxR4fBWTsT8jsxoTRQ8eb9X3hLDh_2ADGktcf_1mlSvdZXsPJt-droEZ3qCg2SPWfiX43sFrnVPSnKTyR513TbHO6tqsoLx4yTkWnUf9ahgEWmHBIYE_jX9UZJQw6GvCVsrXKDmCiqfL7X4e8NPj2GOc8phNLUR0RWSKwQmdC8CStl7JN5Vqh-Zjgy94HCTth1cfRnMH_-Qh4c1-YA09vq53eVZ-Dh4bqio_Qqr29xbTtmbdsMdJXRvCD2M7caTsFzWYSJyPmQN7G_ErN8pX4PUAvOVobRrVBE77tz_g-DZRjfSbmjybDxenwN3keC8Ec-XUl1z6uY4UZM4XQhJznHrxdPJ_x4svDmx0V9btDRPtPYuMIlJaxnIwJiExGoTMFNWZvHWEk6CR5lHOSvSz121-Afpeu9Jm5ZXde9J9OBlgXVopCpczl0JP37GkC-ddngRf9lMUkRARAP9Z-pXUBePNm35Cq2y-KkuC1-J_G4FAz57YYlNy2zqX4DtjzinfZqItA_4JQKaDbcrgf1KQDTUUnoSNC9iO2mC_51LSsP3pseOLV95eJ5Nnt6OFmEizgKYN_U8A5Ktav7mQBNnLfLQx1OPeaq0kYrXErlfOhAxkwjyuK9wofW5XYidV4owr6ED0SDGoDPT7PvAw1_jfbJZGwmpHldnKwClPvDFy9z0mAvlIIdEID7ia36r_pCT7bUiMCNeuK5TDgLQ1lL14yJ8a_YwpPxzJNHw54pF7jZFPAwOAm5VvLikysJpOpSZg_Zjw6SIxEAmU63Arivc38=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c4400001cdf0063_0%7C0a220b774c4800001d928f51_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=E7qbKvVLmYLb2DSc8KAEfk3FxR4fBWTsT8jsxoTRQ8eb9X3hLDh_2ADGktcf_1mlSvdZXsPJt-droEZ3qCg2SPWfiX43sFrnVPSnKTyR513TbHO6tqsoLx4yTkWnUf9ahgEWmHBIYE_jX9UZJQw6GvCVsrXKDmCiqfL7X4e8NPj2GOc8phNLUR0RWSKwQmdC8CStl7JN5Vqh-Zjgy94HCTth1cfRnMH_-Qh4c1-YA09vq53eVZ-Dh4bqio_Qqr29xbTtmbdsMdJXRvCD2M7caTsFzWYSJyPmQN7G_ErN8pX4PUAvOVobRrVBE77tz_g-DZRjfSbmjybDxenwN3keC8Ec-XUl1z6uY4UZM4XQhJznHrxdPJ_x4svDmx0V9btDRPtPYuMIlJaxnIwJiExGoTMFNWZvHWEk6CR5lHOSvSz121-Afpeu9Jm5ZXde9J9OBlgXVopCpczl0JP37GkC-ddngRf9lMUkRARAP9Z-pXUBePNm35Cq2y-KkuC1-J_G4FAz57YYlNy2zqX4DtjzinfZqItA_4JQKaDbcrgf1KQDTUUnoSNC9iO2mC_51LSsP3pseOLV95eJ5Nnt6OFmEizgKYN_U8A5Ktav7mQBNnLfLQx1OPeaq0kYrXErlfOhAxkwjyuK9wofW5XYidV4owr6ED0SDGoDPT7PvAw1_jfbJZGwmpHldnKwClPvDFy9z0mAvlIIdEID7ia36r_pCT7bUiMCNeuK5TDgLQ1lL14yJ8a_YwpPxzJNHw54pF7jZFPAwOAm5VvLikysJpOpSZg_Zjw6SIxEAmU63Arivc38=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-16T19:45:00.000Z", "utc_arrival": "2023-06-16T17:45:00.000Z", "local_departure": "2023-06-16T16:15:00.000Z", "utc_departure": "2023-06-16T14:15:00.000Z"}, {"id": "0b770a224c0b0000d52101c0_0|0a220b774c0e0000c501735e_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 693.785161, "distance": 1975.87, "duration": {"departure": 12600, "return": 11700, "total": 24300}, "price": 205437.5863, "conversion": {"EUR": 537.785551, "HUF": 205437.5863}, "fare": {"adults": 102718.79, "children": 102718.79, "infants": 102718.79}, "bags_price": {"1": 98.42, "2": 196.84}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 439, "hold_height": 149, "hold_length": 171, "hold_weight": 20, "hold_width": 119, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 3}, "airlines": ["W6"], "route": [{"id": "0b770a224c0b0000d52101c0_0", "combination_id": "0b770a224c0b0000d52101c0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "JKREG", "fare_category": "M", "fare_classes": "J", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-20T21:15:00.000Z", "utc_arrival": "2023-04-20T19:15:00.000Z", "local_departure": "2023-04-20T17:45:00.000Z", "utc_departure": "2023-04-20T15:45:00.000Z"}, {"id": "0a220b774c0e0000c501735e_0", "combination_id": "0a220b774c0e0000c501735e", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "JREG", "fare_category": "M", "fare_classes": "J", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-23T21:05:00.000Z", "utc_arrival": "2023-04-23T19:05:00.000Z", "local_departure": "2023-04-23T17:50:00.000Z", "utc_departure": "2023-04-23T15:50:00.000Z"}], "booking_token": "E16-7cZ8O3zQmmXXRCAi-ajh39SZKeStbBfNK6Y6UWZqrBP4xD98dLfIpmraJFyQfqc1NkSdjlFlNQ-6l5tFCTF8P3iY6Zeu-krXznWkVWrGHhBbpVrIBjZVzXzI2Mquyg_oMA7MK_RieDBr3-imik6Zv14f3-DNWT5DBMLMMODTOeOl8YIc7mCI6bPbqPKvgdocb0iPfyLvk-P4LoK56pOM1sylCC4UDJZW6l-ut7WYCxSUKDpBxPDmfSr8Ovah9LCGa2wnUpIKTg1ZeD6m0XiBB0Eelh7YTEuJgUxU1rYFxkHTpsXOOYDXkVUoGmRpadnhV9Dk8OJsC1IzlkiLQJbfItRIdnO01KXSC7qDZlN7ynRDnwwc0b5dh5FxX8EOmsWDZdYcWdSA1__Byfx-CDtk5LavenrREiUU2dgTbVtsoco3cAhG6kOJYavcRFlaD-BPWMvutKkXOArwLEQqaJ6BI6jElJZk4AGUrzVVf59iWGBpFtet6OAhNUHD6NL0OgfsvfSMoXady1X0YBchECCPQHvGrAu2QEl2gljULmC6pVYxB4az-5NM56NABbFrUTxPYS0Ef5SQYlsIbStHmkO3UbrjAqHNdPPKsB4KcQiZ2-veFx3l1AWcDZiXdegg7K2z7zyic3MfUSeAGuWdK7qKPEcwkbtGgBGfYzZ1Le3qGMWUa_BR_NyaGOI7bQyfp9WjMdAlVq8i39H6MzBSDGOTbbSwWhk9eRU4jmK5h7oVq25HEetW07jQN04aTVuBbiKgAdIAJHUsuS4xjpKtSuQ==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c0b0000d52101c0_0%7C0a220b774c0e0000c501735e_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=E16-7cZ8O3zQmmXXRCAi-ajh39SZKeStbBfNK6Y6UWZqrBP4xD98dLfIpmraJFyQfqc1NkSdjlFlNQ-6l5tFCTF8P3iY6Zeu-krXznWkVWrGHhBbpVrIBjZVzXzI2Mquyg_oMA7MK_RieDBr3-imik6Zv14f3-DNWT5DBMLMMODTOeOl8YIc7mCI6bPbqPKvgdocb0iPfyLvk-P4LoK56pOM1sylCC4UDJZW6l-ut7WYCxSUKDpBxPDmfSr8Ovah9LCGa2wnUpIKTg1ZeD6m0XiBB0Eelh7YTEuJgUxU1rYFxkHTpsXOOYDXkVUoGmRpadnhV9Dk8OJsC1IzlkiLQJbfItRIdnO01KXSC7qDZlN7ynRDnwwc0b5dh5FxX8EOmsWDZdYcWdSA1__Byfx-CDtk5LavenrREiUU2dgTbVtsoco3cAhG6kOJYavcRFlaD-BPWMvutKkXOArwLEQqaJ6BI6jElJZk4AGUrzVVf59iWGBpFtet6OAhNUHD6NL0OgfsvfSMoXady1X0YBchECCPQHvGrAu2QEl2gljULmC6pVYxB4az-5NM56NABbFrUTxPYS0Ef5SQYlsIbStHmkO3UbrjAqHNdPPKsB4KcQiZ2-veFx3l1AWcDZiXdegg7K2z7zyic3MfUSeAGuWdK7qKPEcwkbtGgBGfYzZ1Le3qGMWUa_BR_NyaGOI7bQyfp9WjMdAlVq8i39H6MzBSDGOTbbSwWhk9eRU4jmK5h7oVq25HEetW07jQN04aTVuBbiKgAdIAJHUsuS4xjpKtSuQ==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-04-20T21:15:00.000Z", "utc_arrival": "2023-04-20T19:15:00.000Z", "local_departure": "2023-04-20T17:45:00.000Z", "utc_departure": "2023-04-20T15:45:00.000Z"}, {"id": "0b770a224c2c0000f97822f4_0|0a220b774c300000ec1c4165_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 693.375807, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 206809.2327, "conversion": {"EUR": 541.376187, "HUF": 206809.2327}, "fare": {"adults": 103404.62, "children": 103404.62, "infants": 103404.62}, "bags_price": {"1": 69.678, "2": 139.356}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 3}, "airlines": ["FR"], "route": [{"id": "0b770a224c2c0000f97822f4_0", "combination_id": "0b770a224c2c0000f97822f4", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-23T10:15:00.000Z", "utc_arrival": "2023-05-23T08:15:00.000Z", "local_departure": "2023-05-23T06:55:00.000Z", "utc_departure": "2023-05-23T04:55:00.000Z"}, {"id": "0a220b774c300000ec1c4165_0", "combination_id": "0a220b774c300000ec1c4165", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-27T09:40:00.000Z", "utc_arrival": "2023-05-27T07:40:00.000Z", "local_departure": "2023-05-27T06:30:00.000Z", "utc_departure": "2023-05-27T04:30:00.000Z"}], "booking_token": "EhtXkHXimr0ev-p5lp0jDBGo2gbYlDeZK4C9kTVsocqUsHtGnTU3Gv0BpEXYfKJ13gmFt02Lczu6jw6Kn0Cltow3BbE529z2zTJOIuYlS4FYD0VaUBs9ZqfKWMtdTf9q4cuhJfX61Cq7Rq5wOy5HGdxgbOgx04Wd_fjC0gHcQTRHVmo5jo5_xp0Fc_ws_XHrlvqYyslvqrqBZay4JXKP0-9iQjefL1bJ2Qc5rTF1s1FIFkKUGTriTyf6-dA_mPC55eIhSiQNkIFnDeFlbOT5FyPWgiCHEPiMnV22R0J-K_v3-BZxCTyH8Hzvt-hqzCr6d3fYJiv9NwfVeAjfyBcHecc5-tem-oTtikpSVHJOy0qNXdSu2Nb4L5HP2-GjHfMPL_Qxfko5w3b8EHNwClzt38WosMMEr5rNR5wpPuNiNVKWctN29w-a87MfwILtMz--oZjbKv6ReCbYWp_WYxeO9181X2UbZ9Te37MFUtoEQJtHkrh3EiCWzMdO5kO44Ed3W-Fc4AGe6DKsBbpEA3fioJuW9j_fmCYpEp6ygvFuJdw_xyf2pLEz8wAYuFUaQfmg6bruerYM3wLpJ7HwKDXmGLfniMWnfuTIM_NxRLonkHcKI-5KxAW0nvBfIH530tTj9EJ81v8LUa64pzlmimORrkGnYqEGFQ59lnysQ-WTEIHsXZXhn-iEEbrTGP8OPTDQQvnjyeodxCU9KZyudl8KMts3Xyu0VpzCmkcDQGStITDQ=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c2c0000f97822f4_0%7C0a220b774c300000ec1c4165_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EhtXkHXimr0ev-p5lp0jDBGo2gbYlDeZK4C9kTVsocqUsHtGnTU3Gv0BpEXYfKJ13gmFt02Lczu6jw6Kn0Cltow3BbE529z2zTJOIuYlS4FYD0VaUBs9ZqfKWMtdTf9q4cuhJfX61Cq7Rq5wOy5HGdxgbOgx04Wd_fjC0gHcQTRHVmo5jo5_xp0Fc_ws_XHrlvqYyslvqrqBZay4JXKP0-9iQjefL1bJ2Qc5rTF1s1FIFkKUGTriTyf6-dA_mPC55eIhSiQNkIFnDeFlbOT5FyPWgiCHEPiMnV22R0J-K_v3-BZxCTyH8Hzvt-hqzCr6d3fYJiv9NwfVeAjfyBcHecc5-tem-oTtikpSVHJOy0qNXdSu2Nb4L5HP2-GjHfMPL_Qxfko5w3b8EHNwClzt38WosMMEr5rNR5wpPuNiNVKWctN29w-a87MfwILtMz--oZjbKv6ReCbYWp_WYxeO9181X2UbZ9Te37MFUtoEQJtHkrh3EiCWzMdO5kO44Ed3W-Fc4AGe6DKsBbpEA3fioJuW9j_fmCYpEp6ygvFuJdw_xyf2pLEz8wAYuFUaQfmg6bruerYM3wLpJ7HwKDXmGLfniMWnfuTIM_NxRLonkHcKI-5KxAW0nvBfIH530tTj9EJ81v8LUa64pzlmimORrkGnYqEGFQ59lnysQ-WTEIHsXZXhn-iEEbrTGP8OPTDQQvnjyeodxCU9KZyudl8KMts3Xyu0VpzCmkcDQGStITDQ=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-23T10:15:00.000Z", "utc_arrival": "2023-05-23T08:15:00.000Z", "local_departure": "2023-05-23T06:55:00.000Z", "utc_departure": "2023-05-23T04:55:00.000Z"}, {"id": "0b770a224c2b00007aa0884e_0|0a220b774c2e0000ad0adba8_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 694.747393, "distance": 1975.87, "duration": {"departure": 12000, "return": 11700, "total": 23700}, "price": 206823.8467, "conversion": {"EUR": 541.414443, "HUF": 206823.8467}, "fare": {"adults": 103411.92, "children": 106486.91, "infants": 106486.91}, "bags_price": {"1": 69.314, "2": 138.628}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 6}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224c2b00007aa0884e_0", "combination_id": "0b770a224c2b00007aa0884e", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-22T14:00:00.000Z", "utc_arrival": "2023-05-22T12:00:00.000Z", "local_departure": "2023-05-22T10:40:00.000Z", "utc_departure": "2023-05-22T08:40:00.000Z"}, {"id": "0a220b774c2e0000ad0adba8_0", "combination_id": "0a220b774c2e0000ad0adba8", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IJREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-26T01:15:00.000Z", "utc_arrival": "2023-05-25T23:15:00.000Z", "local_departure": "2023-05-25T22:00:00.000Z", "utc_departure": "2023-05-25T20:00:00.000Z"}], "booking_token": "E90ValgTlwd_xy11SiCZO7v_Ke34G2WU4ovOtCV-NP8pFRp1Mu6oiAal73S49zDdYDwcMa2wX5UpXLz1SuvqM0ZlWpVeweEmuQe8Rsk3QpO9E1LKfUcddeDIv6tF1vR1_xyqUhLJ9VNkUGJ-IZogYJUq7-_4ypaXRUMY6sbEmvcuew0BkYLRV59RDHt5De7WKn4nM2_Bp_95vOTJghSHhRtAv7yjqDY6kCJXYk1u6lqtp7PS55vnHUX1i0_ZYNxPxHSo1XQ-8x6mOAbkSfLT-IByfRYqQXNyhJFwHaNSA_1pxtJWq52ZEn3PY5Sj_pSiTCacXlFhPICoEm-Mf9QjLZYOQQX260WQIcnjhNb7kRCQFB_VoZhwGdIKx6efNRrx3OKGgqk70Tsplt-z_nomZOfET7pcE1CZq859JN2gxk0-QcnX5hcqkB5-jGOYqoHmMMVVj1uZw0diM7f3yDkDxmyeXug9j_77WFp-FZBEU05o4nJGzi7feINVpvOIXHKlDiZYVb1CbgeiiS_-8xbvAOJeowoVZlRmOC6VNSEbtfYfefSuiseIH9I_QgA-ymaSEZQ_nwsV4hKAberB2mcdTxqxAxHylTJnu_IcPuaLtGRzuwijBfxdq14sS4SHiMst9zJefSs0l31yoJCbhvNmz4XJlkN8PsY0X-MKD_ZMDMY6UzQ45yDeF5PPLi6ZGRA3YodZu0DgQN2_EA8Md8W6BkiJ4cZJ9tpO8v-cchUvpZfLIPdK5lFUgMQIO0cTObmId4WBzwQlVaX2Zzza8o5Qh4cKXl62F7feCefQI0xB0HgFBdBqEQ_UriSzC_r8JY_8n", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c2b00007aa0884e_0%7C0a220b774c2e0000ad0adba8_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=E90ValgTlwd_xy11SiCZO7v_Ke34G2WU4ovOtCV-NP8pFRp1Mu6oiAal73S49zDdYDwcMa2wX5UpXLz1SuvqM0ZlWpVeweEmuQe8Rsk3QpO9E1LKfUcddeDIv6tF1vR1_xyqUhLJ9VNkUGJ-IZogYJUq7-_4ypaXRUMY6sbEmvcuew0BkYLRV59RDHt5De7WKn4nM2_Bp_95vOTJghSHhRtAv7yjqDY6kCJXYk1u6lqtp7PS55vnHUX1i0_ZYNxPxHSo1XQ-8x6mOAbkSfLT-IByfRYqQXNyhJFwHaNSA_1pxtJWq52ZEn3PY5Sj_pSiTCacXlFhPICoEm-Mf9QjLZYOQQX260WQIcnjhNb7kRCQFB_VoZhwGdIKx6efNRrx3OKGgqk70Tsplt-z_nomZOfET7pcE1CZq859JN2gxk0-QcnX5hcqkB5-jGOYqoHmMMVVj1uZw0diM7f3yDkDxmyeXug9j_77WFp-FZBEU05o4nJGzi7feINVpvOIXHKlDiZYVb1CbgeiiS_-8xbvAOJeowoVZlRmOC6VNSEbtfYfefSuiseIH9I_QgA-ymaSEZQ_nwsV4hKAberB2mcdTxqxAxHylTJnu_IcPuaLtGRzuwijBfxdq14sS4SHiMst9zJefSs0l31yoJCbhvNmz4XJlkN8PsY0X-MKD_ZMDMY6UzQ45yDeF5PPLi6ZGRA3YodZu0DgQN2_EA8Md8W6BkiJ4cZJ9tpO8v-cchUvpZfLIPdK5lFUgMQIO0cTObmId4WBzwQlVaX2Zzza8o5Qh4cKXl62F7feCefQI0xB0HgFBdBqEQ_UriSzC_r8JY_8n", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-22T14:00:00.000Z", "utc_arrival": "2023-05-22T12:00:00.000Z", "local_departure": "2023-05-22T10:40:00.000Z", "utc_departure": "2023-05-22T08:40:00.000Z"}, {"id": "0b770a224bef0000f1a846fa_0|0a220b774bf3000020faa1b2_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 695.09966, "distance": 1975.87, "duration": {"departure": 12000, "return": 11700, "total": 23700}, "price": 206958.415, "conversion": {"EUR": 541.76671, "HUF": 206958.415}, "fare": {"adults": 103479.21, "children": 103479.21, "infants": 103479.21}, "bags_price": {"1": 86.436, "2": 172.872}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 439, "hold_height": 149, "hold_length": 171, "hold_weight": 20, "hold_width": 119, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 2}, "airlines": ["W6"], "route": [{"id": "0b770a224bef0000f1a846fa_0", "combination_id": "0b770a224bef0000f1a846fa", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "KLREG", "fare_category": "M", "fare_classes": "K", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-03-23T19:40:00.000Z", "utc_arrival": "2023-03-23T18:40:00.000Z", "local_departure": "2023-03-23T16:20:00.000Z", "utc_departure": "2023-03-23T15:20:00.000Z"}, {"id": "0a220b774bf3000020faa1b2_0", "combination_id": "0a220b774bf3000020faa1b2", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IJREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-03-27T23:45:00.000Z", "utc_arrival": "2023-03-27T21:45:00.000Z", "local_departure": "2023-03-27T20:30:00.000Z", "utc_departure": "2023-03-27T18:30:00.000Z"}], "booking_token": "EGaymA0591ohaFhe6B77X9ekC04oQyKyqCO0Z_nPONOOqaDA9Y1YTZF99OJfNdvEDr7OK9S1Ff2RYuiMg3W6M7TlgfiRBmuzz7P0HXYxRlbHcdTzA1WTp_1Lk2wjnV8AuC47WvudRBG27LsRf7fsknjrN0UpovWxmSVe09Veq6xlyKy5gDmQ56bit8TPweDqEdpXdwp29dyAg89Xx1MkPKMLyLfMEO7bPiaCk7o1GP4IEUa_ZL93QD2nIdJv6wBbKqYkw0rqZ0hkxqiwIrppDTr7hc-Rbn9_A_bAnzSU7S-uyaqzWd_JvdimCDDfaPzH-pLIa8zHth6R8TYO8cbxqTmxsNIy5-CblzPSiEJkGYqZsyGdVsR8qtpoDVgpv5mHofGc4B9CwBH7JilpWEC_jZvFwx8_bPNtMfxu1i3jutMGAQ4FWvzwDDb3JtNtdvBUAtqBXYZJ0uAD2IqATYGFVXW9OonOf23Or-PgvaKCNnbYZg2Ti8CNQiNvwKhsBAaUkeWdftdxBAoKPR8-j2VCMWhuST4xtpsxasbaZ_E7dFnVjL3FCxUulrfftK8J4Rf1AEhGs33ZN3aRnVmdT7fPYSipXQro1Nn_eRik0gAFSM-dCFFON3zdUOId3gIbhQsKjsscq25ZWz0trfgLHdbNVWiv4uaoB9yQO3bR30_iDvoO1LY84oWvBO8OqI8bHqh7kd4buzCt0PUpWO1PfjXZMBDW8nby3_DzO7GHM2r0BhCK7k9G5-67r-CFLqA78DFHOM8UgBWOCOafJuCjp_AV5GSYL8Ble3mtg6jtcQQhBXkQ=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224bef0000f1a846fa_0%7C0a220b774bf3000020faa1b2_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EGaymA0591ohaFhe6B77X9ekC04oQyKyqCO0Z_nPONOOqaDA9Y1YTZF99OJfNdvEDr7OK9S1Ff2RYuiMg3W6M7TlgfiRBmuzz7P0HXYxRlbHcdTzA1WTp_1Lk2wjnV8AuC47WvudRBG27LsRf7fsknjrN0UpovWxmSVe09Veq6xlyKy5gDmQ56bit8TPweDqEdpXdwp29dyAg89Xx1MkPKMLyLfMEO7bPiaCk7o1GP4IEUa_ZL93QD2nIdJv6wBbKqYkw0rqZ0hkxqiwIrppDTr7hc-Rbn9_A_bAnzSU7S-uyaqzWd_JvdimCDDfaPzH-pLIa8zHth6R8TYO8cbxqTmxsNIy5-CblzPSiEJkGYqZsyGdVsR8qtpoDVgpv5mHofGc4B9CwBH7JilpWEC_jZvFwx8_bPNtMfxu1i3jutMGAQ4FWvzwDDb3JtNtdvBUAtqBXYZJ0uAD2IqATYGFVXW9OonOf23Or-PgvaKCNnbYZg2Ti8CNQiNvwKhsBAaUkeWdftdxBAoKPR8-j2VCMWhuST4xtpsxasbaZ_E7dFnVjL3FCxUulrfftK8J4Rf1AEhGs33ZN3aRnVmdT7fPYSipXQro1Nn_eRik0gAFSM-dCFFON3zdUOId3gIbhQsKjsscq25ZWz0trfgLHdbNVWiv4uaoB9yQO3bR30_iDvoO1LY84oWvBO8OqI8bHqh7kd4buzCt0PUpWO1PfjXZMBDW8nby3_DzO7GHM2r0BhCK7k9G5-67r-CFLqA78DFHOM8UgBWOCOafJuCjp_AV5GSYL8Ble3mtg6jtcQQhBXkQ=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-03-23T19:40:00.000Z", "utc_arrival": "2023-03-23T18:40:00.000Z", "local_departure": "2023-03-23T16:20:00.000Z", "utc_departure": "2023-03-23T15:20:00.000Z"}, {"id": "0b770a224bfa0000f711598b_0|0a220b774bfe0000f8408ba8_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 703.301871, "distance": 1975.87, "duration": {"departure": 12600, "return": 12900, "total": 25500}, "price": 207035.6686, "conversion": {"EUR": 541.968941, "HUF": 207035.6686}, "fare": {"adults": 103517.83, "children": 103517.83, "infants": 103517.83}, "bags_price": {"1": 113.624, "2": 227.234}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 439, "hold_height": 149, "hold_length": 171, "hold_weight": 20, "hold_width": 119, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 2}, "airlines": ["W6"], "route": [{"id": "0b770a224bfa0000f711598b_0", "combination_id": "0b770a224bfa0000f711598b", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "JKREG", "fare_category": "M", "fare_classes": "J", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-03T19:45:00.000Z", "utc_arrival": "2023-04-03T17:45:00.000Z", "local_departure": "2023-04-03T16:15:00.000Z", "utc_departure": "2023-04-03T14:15:00.000Z"}, {"id": "0a220b774bfe0000f8408ba8_0", "combination_id": "0a220b774bfe0000f8408ba8", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "JKREG", "fare_category": "M", "fare_classes": "J", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-08T00:05:00.000Z", "utc_arrival": "2023-04-07T22:05:00.000Z", "local_departure": "2023-04-07T20:30:00.000Z", "utc_departure": "2023-04-07T18:30:00.000Z"}], "booking_token": "ECDY_DOpZEoU8vASSouYNRABWqXTKvK4G_8DodtGiFQj8tpGHiILzURNqGepYg0JMITuT7jEldRrME7BoaOEoYyyGpqWx-PbaV7XpnbQ6y3J7DnfDqy2PYg-PG1z9tpby-XO8YvkbZ0qQvTHQVyU67lVEb-yhCr76cTICbKh9_2yaup-64N8iSa-hTp_7J2S8xqoY6IiDrstBb0UJ8aA6Tcx5PYTw6Uwh559uUbkXj45izftJbilY-Z7VddZVBjDmKKvecQwDjlodTYwRujbL5b-48iJ6J04L0gsRMG6_pvESN1hWqlTqxXQ5LbU_wQ1VqLzvuaQt5qN3p7C-37cqFEnFBDogEi5FUl3kXCyMbJDXb4MLBVy1lOFcOZVAiwYR-foZJKnqUHQA5ve55IGbW0dLK4qXu2VRKzuTNR2jCj9DFCicv5VYGP9fn9b9kTvD1qST0mp9ZMnBrcx4JYfJQOGKQAQgepEzYACGSLiKXvQusrmAoJEFVWE__jUkACQMPiJiBQAzkewvO03UgeVKfbKea8VJR1K7UECl9SUv1fF_gFdkQn0Qxq2JrZsLtb4nVccwrHG7R8JzHqz4ogXpZ-yd20QFT0tX1cVAdPaC2NdYphtXFHrrl_Oh5G7xBSZ6Xh3XxPycD7kNfA8wL-pgGy17aEW4cECMzX17y4--jrDHCe4ig7hUoishhDP3OU0299496KcKcTjdg2QaUNqmwYDweeKyJ5calALAuwB9a-tEyMZHoo6IffKU3Q7fnd_RY3xRvb3vAPmJdjD5n5nC5Q==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224bfa0000f711598b_0%7C0a220b774bfe0000f8408ba8_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=ECDY_DOpZEoU8vASSouYNRABWqXTKvK4G_8DodtGiFQj8tpGHiILzURNqGepYg0JMITuT7jEldRrME7BoaOEoYyyGpqWx-PbaV7XpnbQ6y3J7DnfDqy2PYg-PG1z9tpby-XO8YvkbZ0qQvTHQVyU67lVEb-yhCr76cTICbKh9_2yaup-64N8iSa-hTp_7J2S8xqoY6IiDrstBb0UJ8aA6Tcx5PYTw6Uwh559uUbkXj45izftJbilY-Z7VddZVBjDmKKvecQwDjlodTYwRujbL5b-48iJ6J04L0gsRMG6_pvESN1hWqlTqxXQ5LbU_wQ1VqLzvuaQt5qN3p7C-37cqFEnFBDogEi5FUl3kXCyMbJDXb4MLBVy1lOFcOZVAiwYR-foZJKnqUHQA5ve55IGbW0dLK4qXu2VRKzuTNR2jCj9DFCicv5VYGP9fn9b9kTvD1qST0mp9ZMnBrcx4JYfJQOGKQAQgepEzYACGSLiKXvQusrmAoJEFVWE__jUkACQMPiJiBQAzkewvO03UgeVKfbKea8VJR1K7UECl9SUv1fF_gFdkQn0Qxq2JrZsLtb4nVccwrHG7R8JzHqz4ogXpZ-yd20QFT0tX1cVAdPaC2NdYphtXFHrrl_Oh5G7xBSZ6Xh3XxPycD7kNfA8wL-pgGy17aEW4cECMzX17y4--jrDHCe4ig7hUoishhDP3OU0299496KcKcTjdg2QaUNqmwYDweeKyJ5calALAuwB9a-tEyMZHoo6IffKU3Q7fnd_RY3xRvb3vAPmJdjD5n5nC5Q==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-04-03T19:45:00.000Z", "utc_arrival": "2023-04-03T17:45:00.000Z", "local_departure": "2023-04-03T16:15:00.000Z", "utc_departure": "2023-04-03T14:15:00.000Z"}, {"id": "0b770a224c330000e6ceb6e5_0|0a220b774c36000010c6991f_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 694.757452, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 207337.0301, "conversion": {"EUR": 542.757832, "HUF": 207337.0301}, "fare": {"adults": 103668.52, "children": 108031.91, "infants": 108031.91}, "bags_price": {"1": 69.678, "2": 139.356}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 3}, "airlines": ["FR"], "route": [{"id": "0b770a224c330000e6ceb6e5_0", "combination_id": "0b770a224c330000e6ceb6e5", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-30T10:15:00.000Z", "utc_arrival": "2023-05-30T08:15:00.000Z", "local_departure": "2023-05-30T06:55:00.000Z", "utc_departure": "2023-05-30T04:55:00.000Z"}, {"id": "0a220b774c36000010c6991f_0", "combination_id": "0a220b774c36000010c6991f", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-02T18:00:00.000Z", "utc_arrival": "2023-06-02T16:00:00.000Z", "local_departure": "2023-06-02T14:50:00.000Z", "utc_departure": "2023-06-02T12:50:00.000Z"}], "booking_token": "Ex4rdJbHm0ez_7e-8KdHbkQPp3qnQFoFT_toa8hwf5ZoHEF8W8S0iHeuYHGpYi8jYHelmOrh7tx0yxZfEX5Ydqo93SnGMLlV4VNB-ptY1DAERLeuAR4uNLow9xfcvD1bqH8WYZK_r4o0_UFwrYPPK5UXknl0wfptmXbIIL3Qeyq91tAdKb4v2KXx1rtxxchMhaXShIK3sArztv4wFxcNESMpTqkAyfaEYkQ5c0Op_AHQybN1tmrPTKRWiEP9FvB3EeAQPrL1oujFj22hOxCTbQtNndwX9dyIvJjHtYfk60df0yAo3fYeKYnNo8bIJMEq7g5kREVo3cVgkM9HvK20pwQe37PTiEori1kQry1kNXbwHJ5UrH4jYqmVYTRfiflhFYTqD9NLJd-uwsovBzNmKCpveYp7cmQSqd0SgkftD2LVrCZuvD1prFdugiAKjzhDn8T38exwNCmytJoPCLLfsJSviGDvGkl1IWB49DAa3IkeMAkagtjIRdJmFU8HAD__4o2cZpMrmeyGhr1pU1pYh7GTi4y2ze3tPLfW0sxPavXH9s0Hur9rO56XcT1YaS5hT7kbFU_-Tw8pLrXX1Xuo31ecOAwMMI1A2X936gXxsO0keTgGtQFXjNCadGH6CpK_QkDaUIsbXItaGA22-mHKt5skTV0J-qirugOuMiun73H1V3cmsXa6JYpBYSXmzgVabIcapdoouXKXeds5YGoqBiL4JSJ4rnRPvq1cMM7oPsVz5lrolftS11sgHFGVY6nB5", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c330000e6ceb6e5_0%7C0a220b774c36000010c6991f_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=Ex4rdJbHm0ez_7e-8KdHbkQPp3qnQFoFT_toa8hwf5ZoHEF8W8S0iHeuYHGpYi8jYHelmOrh7tx0yxZfEX5Ydqo93SnGMLlV4VNB-ptY1DAERLeuAR4uNLow9xfcvD1bqH8WYZK_r4o0_UFwrYPPK5UXknl0wfptmXbIIL3Qeyq91tAdKb4v2KXx1rtxxchMhaXShIK3sArztv4wFxcNESMpTqkAyfaEYkQ5c0Op_AHQybN1tmrPTKRWiEP9FvB3EeAQPrL1oujFj22hOxCTbQtNndwX9dyIvJjHtYfk60df0yAo3fYeKYnNo8bIJMEq7g5kREVo3cVgkM9HvK20pwQe37PTiEori1kQry1kNXbwHJ5UrH4jYqmVYTRfiflhFYTqD9NLJd-uwsovBzNmKCpveYp7cmQSqd0SgkftD2LVrCZuvD1prFdugiAKjzhDn8T38exwNCmytJoPCLLfsJSviGDvGkl1IWB49DAa3IkeMAkagtjIRdJmFU8HAD__4o2cZpMrmeyGhr1pU1pYh7GTi4y2ze3tPLfW0sxPavXH9s0Hur9rO56XcT1YaS5hT7kbFU_-Tw8pLrXX1Xuo31ecOAwMMI1A2X936gXxsO0keTgGtQFXjNCadGH6CpK_QkDaUIsbXItaGA22-mHKt5skTV0J-qirugOuMiun73H1V3cmsXa6JYpBYSXmzgVabIcapdoouXKXeds5YGoqBiL4JSJ4rnRPvq1cMM7oPsVz5lrolftS11sgHFGVY6nB5", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-30T10:15:00.000Z", "utc_arrival": "2023-05-30T08:15:00.000Z", "local_departure": "2023-05-30T06:55:00.000Z", "utc_departure": "2023-05-30T04:55:00.000Z"}, {"id": "0b770a224c3e0000d8f9b259_0|0a220b774c4100004abd18f4_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 698.734494, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 208856.286, "conversion": {"EUR": 546.734874, "HUF": 208856.286}, "fare": {"adults": 104428.14, "children": 104428.14, "infants": 104428.14}, "bags_price": {"1": 76.706, "2": 163.212}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 158, "hold_height": 52, "hold_length": 78, "hold_weight": 20, "hold_width": 28, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 3, "personal_item_width": 15}, "availability": {"seats": 6}, "airlines": ["FR", "IB"], "route": [{"id": "0b770a224c3e0000d8f9b259_0", "combination_id": "0b770a224c3e0000d8f9b259", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-10T13:25:00.000Z", "utc_arrival": "2023-06-10T11:25:00.000Z", "local_departure": "2023-06-10T10:05:00.000Z", "utc_departure": "2023-06-10T08:05:00.000Z"}, {"id": "0a220b774c4100004abd18f4_0", "combination_id": "0a220b774c4100004abd18f4", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "IB", "flight_no": 3278, "operating_carrier": "IB", "operating_flight_no": "3278", "fare_basis": "NWNNAOB4", "fare_category": "M", "fare_classes": "N", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-13T14:55:00.000Z", "utc_arrival": "2023-06-13T12:55:00.000Z", "local_departure": "2023-06-13T11:45:00.000Z", "utc_departure": "2023-06-13T09:45:00.000Z"}], "booking_token": "ENCoKq5oqhasCunYNhn0qjAYdMOQ8w1XDbtR6RvqSmKqOT5Hnde8Vb3Qq5v5jXGW5YptIYk99M4ejeIEV4SdPpX95vFWDzSJV4pONI-1_S60md0-ZrX4hCjO_RY12w_0IhB85Ri2QLSolU3CbfEAdRMtqDnyk8NwJIRh8hI3tgFClrX1b9z01mP0huZXtvyHgnabb3rEjYIZT2HYwczVg8ytOjzCKSJYAIadDw4q1N0JcI090Ot1HwV6EdyfGNbIgOSeax1JsHFWf1KVoA5T1vumRH6jIoi_xewVVzGu_CamUB_WQtf6WaGlY26K-c5f8PAVovYCDIMBbzIlL4F90FizFWsauzOy9czqf5wissuFqynf5PZyobG1F20sKjtOCGV65yf9HmQwW20CLANbgdpzqrbIP6QahWu88GLcOJ4IlhS4r_PhUFwbtw96zIBWG9TKmoEqfaCr1zAbt9RiMuvs8C09Q7jMFvsIZgkQCyNn60wz390SjCHInu4rY-hRsoXUbwkhStvnpDjSwKthOJLvjX1inPrIMqfsQzuPaJK_MCEyYjCAH6oEqWB-c7WxRjkpXCm7EyNIENZOgpu0Bd5uClJRbOdSgs1c8t3JCc4juocG1mZvWSqIwgBi7UYkVDJrWsFf9OCIM1ISBC_IFW4avAf2TtPsN2EztGnvIk66xsbdMfa2Ic08ezkd3b0GKZouNMsGMH1e-0jhr4lhIyCzsHWDZrkdL63vvDKWaC6BLcGbFRu4yDRtC_q17bnK_", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c3e0000d8f9b259_0%7C0a220b774c4100004abd18f4_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=ENCoKq5oqhasCunYNhn0qjAYdMOQ8w1XDbtR6RvqSmKqOT5Hnde8Vb3Qq5v5jXGW5YptIYk99M4ejeIEV4SdPpX95vFWDzSJV4pONI-1_S60md0-ZrX4hCjO_RY12w_0IhB85Ri2QLSolU3CbfEAdRMtqDnyk8NwJIRh8hI3tgFClrX1b9z01mP0huZXtvyHgnabb3rEjYIZT2HYwczVg8ytOjzCKSJYAIadDw4q1N0JcI090Ot1HwV6EdyfGNbIgOSeax1JsHFWf1KVoA5T1vumRH6jIoi_xewVVzGu_CamUB_WQtf6WaGlY26K-c5f8PAVovYCDIMBbzIlL4F90FizFWsauzOy9czqf5wissuFqynf5PZyobG1F20sKjtOCGV65yf9HmQwW20CLANbgdpzqrbIP6QahWu88GLcOJ4IlhS4r_PhUFwbtw96zIBWG9TKmoEqfaCr1zAbt9RiMuvs8C09Q7jMFvsIZgkQCyNn60wz390SjCHInu4rY-hRsoXUbwkhStvnpDjSwKthOJLvjX1inPrIMqfsQzuPaJK_MCEyYjCAH6oEqWB-c7WxRjkpXCm7EyNIENZOgpu0Bd5uClJRbOdSgs1c8t3JCc4juocG1mZvWSqIwgBi7UYkVDJrWsFf9OCIM1ISBC_IFW4avAf2TtPsN2EztGnvIk66xsbdMfa2Ic08ezkd3b0GKZouNMsGMH1e-0jhr4lhIyCzsHWDZrkdL63vvDKWaC6BLcGbFRu4yDRtC_q17bnK_", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-10T13:25:00.000Z", "utc_arrival": "2023-06-10T11:25:00.000Z", "local_departure": "2023-06-10T10:05:00.000Z", "utc_departure": "2023-06-10T08:05:00.000Z"}, {"id": "0b770a224c0b0000d52101c0_0|0a220b774c0f00005b6aa57a_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 703.78499, "distance": 1975.87, "duration": {"departure": 12600, "return": 11700, "total": 24300}, "price": 209257.5862, "conversion": {"EUR": 547.78538, "HUF": 209257.5862}, "fare": {"adults": 104628.79, "children": 108334.04, "infants": 108334.04}, "bags_price": {"1": 98.42, "2": 196.84}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 439, "hold_height": 149, "hold_length": 171, "hold_weight": 20, "hold_width": 119, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 6}, "airlines": ["W6"], "route": [{"id": "0b770a224c0b0000d52101c0_0", "combination_id": "0b770a224c0b0000d52101c0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "JKREG", "fare_category": "M", "fare_classes": "J", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-20T21:15:00.000Z", "utc_arrival": "2023-04-20T19:15:00.000Z", "local_departure": "2023-04-20T17:45:00.000Z", "utc_departure": "2023-04-20T15:45:00.000Z"}, {"id": "0a220b774c0f00005b6aa57a_0", "combination_id": "0a220b774c0f00005b6aa57a", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IJREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-24T23:45:00.000Z", "utc_arrival": "2023-04-24T21:45:00.000Z", "local_departure": "2023-04-24T20:30:00.000Z", "utc_departure": "2023-04-24T18:30:00.000Z"}], "booking_token": "EFnCbJklhe4D1wG7tLxulVesNA96PjzyLMRUXD5YAy9cd0vsrKN5uLN0-5rCkRU1Y5_TGvztv9HC7tQ8WDtmmnj1ChrB9g8jweQ0cOjavZ-WvW7Lj_A7oafaeMo3hE_9X7raPgc0ycxNc_T3msNUTpksCbkuROaQ7LEKJdSQtoIvPlLX2WyHPiuh2Yt10EqiUw3RCXf4ZYr7wmhpNhVGx4HnPsXmNrUZNBCZoRHmBusiz8VOb9XDCdd553DfQ_Q8FlsTb7bgRcLnyW-jgKOp_8E6s3ORBJ8E7JIeYLMUNy8N5dwSsfksG22ODD6bBubAVnodu20HTg6F6rKY1cFc6C8krr2RmBbfw4Crb9YPOqkbOQbj490pOCJIokEK0jX10ikhQdo4TssvzDL_0FfS-HXZ5Vj77CwuVJu9TWEpLRHgk_bkGlsV-uuiI33lZVBpcHn-qZ4PfQuDElqVxH8qbSkxBeCJ0jNt3oP11LpqHH8JV-KJb_3PKlzmcjY9hbp4lPW1iH2Q8VmX86gGDftoxgUkOuQ69Y5X2byasa4B54yqYRgJcnOmhOZ3kBm_XjmqxWUFFLL10mpqYpcMZ7T2wxKTfE3dZOHwey24oQAnH3_1qJNjaK1lGwdmjS_dCxukcKJoFLUbtP3CYqD2aZRjR1LcSR75JBtDfa9bUVA1_5TnAccObMyg2b5EG7Tdliy8DS9oGR_hrjcsDOt3hUg3g8DRhi_jNE7Es_aAPHkskwzEcNgfayNf-MLCxxfikKYwETPuroEcScfCOp5J5qHzppKlm1tzDaVf81fdh-KI_RAc=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c0b0000d52101c0_0%7C0a220b774c0f00005b6aa57a_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EFnCbJklhe4D1wG7tLxulVesNA96PjzyLMRUXD5YAy9cd0vsrKN5uLN0-5rCkRU1Y5_TGvztv9HC7tQ8WDtmmnj1ChrB9g8jweQ0cOjavZ-WvW7Lj_A7oafaeMo3hE_9X7raPgc0ycxNc_T3msNUTpksCbkuROaQ7LEKJdSQtoIvPlLX2WyHPiuh2Yt10EqiUw3RCXf4ZYr7wmhpNhVGx4HnPsXmNrUZNBCZoRHmBusiz8VOb9XDCdd553DfQ_Q8FlsTb7bgRcLnyW-jgKOp_8E6s3ORBJ8E7JIeYLMUNy8N5dwSsfksG22ODD6bBubAVnodu20HTg6F6rKY1cFc6C8krr2RmBbfw4Crb9YPOqkbOQbj490pOCJIokEK0jX10ikhQdo4TssvzDL_0FfS-HXZ5Vj77CwuVJu9TWEpLRHgk_bkGlsV-uuiI33lZVBpcHn-qZ4PfQuDElqVxH8qbSkxBeCJ0jNt3oP11LpqHH8JV-KJb_3PKlzmcjY9hbp4lPW1iH2Q8VmX86gGDftoxgUkOuQ69Y5X2byasa4B54yqYRgJcnOmhOZ3kBm_XjmqxWUFFLL10mpqYpcMZ7T2wxKTfE3dZOHwey24oQAnH3_1qJNjaK1lGwdmjS_dCxukcKJoFLUbtP3CYqD2aZRjR1LcSR75JBtDfa9bUVA1_5TnAccObMyg2b5EG7Tdliy8DS9oGR_hrjcsDOt3hUg3g8DRhi_jNE7Es_aAPHkskwzEcNgfayNf-MLCxxfikKYwETPuroEcScfCOp5J5qHzppKlm1tzDaVf81fdh-KI_RAc=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-04-20T21:15:00.000Z", "utc_arrival": "2023-04-20T19:15:00.000Z", "local_departure": "2023-04-20T17:45:00.000Z", "utc_departure": "2023-04-20T15:45:00.000Z"}, {"id": "0b770a224c1a0000e8ad793c_0|0a220b774c1e00004eb45e85_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 700.106166, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 209380.2737, "conversion": {"EUR": 548.106546, "HUF": 209380.2737}, "fare": {"adults": 104690.14, "children": 104690.14, "infants": 104690.14}, "bags_price": {"1": 71.288, "2": 142.59}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 6}, "airlines": ["FR"], "route": [{"id": "0b770a224c1a0000e8ad793c_0", "combination_id": "0b770a224c1a0000e8ad793c", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-05T21:45:00.000Z", "utc_arrival": "2023-05-05T19:45:00.000Z", "local_departure": "2023-05-05T18:25:00.000Z", "utc_departure": "2023-05-05T16:25:00.000Z"}, {"id": "0a220b774c1e00004eb45e85_0", "combination_id": "0a220b774c1e00004eb45e85", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-09T14:05:00.000Z", "utc_arrival": "2023-05-09T12:05:00.000Z", "local_departure": "2023-05-09T10:55:00.000Z", "utc_departure": "2023-05-09T08:55:00.000Z"}], "booking_token": "EXaiSUup6et7c65dVgAQw-MPBHKJQh1pkc_25gc2b_HBlOkiWs6AhZdadK2kJDs-76YzQzIrCljHIFVgH4w-Mg09kbOa8G8ysh14GOGYwoDijor1J1PPdQoqkYbw5bGDoGbBDfafjs1N5xa4O4kOICKTyuD4MicVOiUPag05KxhFZneJMgw56oHqDN8nMeo5E5Y-NmS4HC7chkhXELoSSS0Tbe6y_maRi7TAR2rnNofysuCeiwVEY094-PVM4boOI1V6gHH_vuAFwsFpGksvNdEYaSkLsLAH4tbCDZV5vDtO7-9X4S5NrkCQDOqYpC0fy1gO_Sg0RmxQsBhwvbtLik-RepjbYYrZ3vvYEmWhsjhdwOtu2QYmHN-VTEI4u1Ft4ERFzWWQoEB6PJNWFW_uKtrYqPdX5Q2iLnBW5o7J5k9Su_OwKnd11bo7AGvZEPmhdLVBLXaT5GA78qlofDeK6tK5EIansadtPPY9LMonvpNs28r3_rHAzrf3Vku41p4Tmw4nBDRpN2R7AlYfAXyKI-s96ChJjv9Ezz_fgmzcdVXVGnOCOjHxf5LOXNFEWUs8byvPyOd6qUPZE96JG8k1aiIY5WqmnfhrxGR39PrSyNUYcA6bA0T6hxcm1BWRpC_KD-ze4En4f2d2XMwtEJjmUccqb-a4XVVrrcK2Ibd7j9oB1lsKftW5JzSZbzQSso_K_0WzEk2rk3HVNf7fA6pPrX0RkVDz0abl8G8TVuuKXNq4=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c1a0000e8ad793c_0%7C0a220b774c1e00004eb45e85_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EXaiSUup6et7c65dVgAQw-MPBHKJQh1pkc_25gc2b_HBlOkiWs6AhZdadK2kJDs-76YzQzIrCljHIFVgH4w-Mg09kbOa8G8ysh14GOGYwoDijor1J1PPdQoqkYbw5bGDoGbBDfafjs1N5xa4O4kOICKTyuD4MicVOiUPag05KxhFZneJMgw56oHqDN8nMeo5E5Y-NmS4HC7chkhXELoSSS0Tbe6y_maRi7TAR2rnNofysuCeiwVEY094-PVM4boOI1V6gHH_vuAFwsFpGksvNdEYaSkLsLAH4tbCDZV5vDtO7-9X4S5NrkCQDOqYpC0fy1gO_Sg0RmxQsBhwvbtLik-RepjbYYrZ3vvYEmWhsjhdwOtu2QYmHN-VTEI4u1Ft4ERFzWWQoEB6PJNWFW_uKtrYqPdX5Q2iLnBW5o7J5k9Su_OwKnd11bo7AGvZEPmhdLVBLXaT5GA78qlofDeK6tK5EIansadtPPY9LMonvpNs28r3_rHAzrf3Vku41p4Tmw4nBDRpN2R7AlYfAXyKI-s96ChJjv9Ezz_fgmzcdVXVGnOCOjHxf5LOXNFEWUs8byvPyOd6qUPZE96JG8k1aiIY5WqmnfhrxGR39PrSyNUYcA6bA0T6hxcm1BWRpC_KD-ze4En4f2d2XMwtEJjmUccqb-a4XVVrrcK2Ibd7j9oB1lsKftW5JzSZbzQSso_K_0WzEk2rk3HVNf7fA6pPrX0RkVDz0abl8G8TVuuKXNq4=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-05T21:45:00.000Z", "utc_arrival": "2023-05-05T19:45:00.000Z", "local_departure": "2023-05-05T18:25:00.000Z", "utc_departure": "2023-05-05T16:25:00.000Z"}, {"id": "0b770a224bef0000f1a846fa_0|0a220b774bf30000da5652ad_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 700.518819, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 209537.9098, "conversion": {"EUR": 548.519199, "HUF": 209537.9098}, "fare": {"adults": 104768.95, "children": 104768.95, "infants": 104768.95}, "bags_price": {"1": 95.522, "2": 191.044}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 2}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224bef0000f1a846fa_0", "combination_id": "0b770a224bef0000f1a846fa", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "KLREG", "fare_category": "M", "fare_classes": "K", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-03-23T19:40:00.000Z", "utc_arrival": "2023-03-23T18:40:00.000Z", "local_departure": "2023-03-23T16:20:00.000Z", "utc_departure": "2023-03-23T15:20:00.000Z"}, {"id": "0a220b774bf30000da5652ad_0", "combination_id": "0a220b774bf30000da5652ad", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-03-27T10:15:00.000Z", "utc_arrival": "2023-03-27T08:15:00.000Z", "local_departure": "2023-03-27T07:05:00.000Z", "utc_departure": "2023-03-27T05:05:00.000Z"}], "booking_token": "E7n3WbRLi4wlsiBLW7jp9b1jsd5T4deXIo6uW9FVarwtEwVfr8_CoDstDCPrM058w1zclL8KvtNzBwC6DphTW2ZQuN2lW3NmMHnaCoT78PgSEvOn8WintI0I8drhGKa5NW9jEwwRlmEjbHPtW0LDtoh94xJZgb925oGZzJ4rluFgexALOj1eaUtmntUUf-6oIGLaFA1ij_9iRTZeoN7tDS6dTZseuNC1nKQeCs-FvOMmUfMTyQVfhXdxT6tA2wyVBvUtBr_Il-uAv17BGBeIuJBdni4k4GmC8wB3jCjzpTJzlJ_v5pSsR7iHil9IntNN9P9ruWGKcMPcXOLnZ65kjGlaOnceFrrNrMYMqxTgIV1xfQz9DleOEbfQR8yTd5drh2SeK7JfmQdbPWDck3S6PZXY9uUfyt8du58nMfvJH_ii40I1HqISCfJx16l1LikmwIx1nepxIPjKJ35VzMB1YBzEGcKw_mCZHmMlS9ID0D1vL9nDhd1yCtNNosVCWIVxJgn6XTidonAEyKFTZ8_p4Wm0Zy4o2NdQJzlYbpl_A-vwtOKj0rMIRGf98mTDmM-yIT1u5zeI4YIywMHgpIn6-ybYBKiVs9-53WZ94OBw5PN5JywmMWztDgHe6wgWVtn9bFRvzKJc8kCqkZEQ-OnHKDqMSsAr7A3liNbEzJ0_GI6sxGNun3sJcd2EBzYkgCuFgzmEySf7Vh8W6qj0h0BHqBi94j83a9RTy7x-2UU14uSdIdj3Qt5xpaj2OFEOy61CmNY8Kepolny5KBJW3seykvkcQbxatrL4iL4I9XxbYCrc=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224bef0000f1a846fa_0%7C0a220b774bf30000da5652ad_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=E7n3WbRLi4wlsiBLW7jp9b1jsd5T4deXIo6uW9FVarwtEwVfr8_CoDstDCPrM058w1zclL8KvtNzBwC6DphTW2ZQuN2lW3NmMHnaCoT78PgSEvOn8WintI0I8drhGKa5NW9jEwwRlmEjbHPtW0LDtoh94xJZgb925oGZzJ4rluFgexALOj1eaUtmntUUf-6oIGLaFA1ij_9iRTZeoN7tDS6dTZseuNC1nKQeCs-FvOMmUfMTyQVfhXdxT6tA2wyVBvUtBr_Il-uAv17BGBeIuJBdni4k4GmC8wB3jCjzpTJzlJ_v5pSsR7iHil9IntNN9P9ruWGKcMPcXOLnZ65kjGlaOnceFrrNrMYMqxTgIV1xfQz9DleOEbfQR8yTd5drh2SeK7JfmQdbPWDck3S6PZXY9uUfyt8du58nMfvJH_ii40I1HqISCfJx16l1LikmwIx1nepxIPjKJ35VzMB1YBzEGcKw_mCZHmMlS9ID0D1vL9nDhd1yCtNNosVCWIVxJgn6XTidonAEyKFTZ8_p4Wm0Zy4o2NdQJzlYbpl_A-vwtOKj0rMIRGf98mTDmM-yIT1u5zeI4YIywMHgpIn6-ybYBKiVs9-53WZ94OBw5PN5JywmMWztDgHe6wgWVtn9bFRvzKJc8kCqkZEQ-OnHKDqMSsAr7A3liNbEzJ0_GI6sxGNun3sJcd2EBzYkgCuFgzmEySf7Vh8W6qj0h0BHqBi94j83a9RTy7x-2UU14uSdIdj3Qt5xpaj2OFEOy61CmNY8Kepolny5KBJW3seykvkcQbxatrL4iL4I9XxbYCrc=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-03-23T19:40:00.000Z", "utc_arrival": "2023-03-23T18:40:00.000Z", "local_departure": "2023-03-23T16:20:00.000Z", "utc_departure": "2023-03-23T15:20:00.000Z"}, {"id": "0b770a224c4c0000c66587fd_0|0a220b774c5000001f0cf151_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 700.689019, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 209602.9273, "conversion": {"EUR": 548.689399, "HUF": 209602.9273}, "fare": {"adults": 104801.46, "children": 104801.46, "infants": 104801.46}, "bags_price": {"1": 86.114, "2": 182.028}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 158, "hold_height": 52, "hold_length": 78, "hold_weight": 20, "hold_width": 28, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 3, "personal_item_width": 15}, "availability": {"seats": 2}, "airlines": ["FR", "IB"], "route": [{"id": "0b770a224c4c0000c66587fd_0", "combination_id": "0b770a224c4c0000c66587fd", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-24T13:25:00.000Z", "utc_arrival": "2023-06-24T11:25:00.000Z", "local_departure": "2023-06-24T10:05:00.000Z", "utc_departure": "2023-06-24T08:05:00.000Z"}, {"id": "0a220b774c5000001f0cf151_0", "combination_id": "0a220b774c5000001f0cf151", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "IB", "flight_no": 3278, "operating_carrier": "IB", "operating_flight_no": "3278", "fare_basis": "QZNNAOB4", "fare_category": "M", "fare_classes": "Q", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-28T14:55:00.000Z", "utc_arrival": "2023-06-28T12:55:00.000Z", "local_departure": "2023-06-28T11:45:00.000Z", "utc_departure": "2023-06-28T09:45:00.000Z"}], "booking_token": "E-EQXhw-v_3mBNa-C8GWAXVZyxaeOFb6uLkKcjpSYP3l4R36E682z_FM__CCfipuL1TfsbswVNkhFomtnsyNEHNjGTqzcmBpPmHPl6OzQ5cy1ur2YhzWsCBzWAm7EutFzBmMm-aKmum6eHJI8h_A0WxkqyEWu0X9MJ81lWcrREvtIcoslQ0GWD5qxDKcABEpZ3Tlv9p9dTrVjhErzsMdByPuVZmH_S1PtqukYPmXAku6FOdm1pmSDNgecLHSP0AMh3HDJlfsWKkWt2y0j9KcndmKb8LuaH1H4A_od8n6eWW6aAwodU7hy1swS_jAAV73pPyt-DthXacfFiT6-OurNe2mQbZ_sI2Y4ltDT_vc7q0nbYcXGvi_OitTuffdLObUXLLIwPAE66FLIDVFabU3baHowvm7YzQ_fzd-sWO_ct7Ph85M7UF5q2-2YYA342pmhk4FoK7fxA0HlxDpZI5ojVFQ2ZomciRTjYRNaXUb721kZmikdzxKqn90OUMDQ9TGOH5bU83Ms07jPQnUfDjVvyrFCQPz_Naa7nrcGL19kOXc4MqVLTkVUz02uubxFaVbZSmCynSAXBcRhQujGIfeTZPRY7WxOaETHhWx3OTpPqMJpK23mK-4u_nib1IlqvbuB_CWXMD3thoTKc-9_YhB3muLndhsLJE3i2Ka9D3kx6pzkbGhHizbuwY3cQQhpSFbok28YCVXwddDzOH2KF-J5NKXVi0zCwAXY5EMyuV85Djg=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c4c0000c66587fd_0%7C0a220b774c5000001f0cf151_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=E-EQXhw-v_3mBNa-C8GWAXVZyxaeOFb6uLkKcjpSYP3l4R36E682z_FM__CCfipuL1TfsbswVNkhFomtnsyNEHNjGTqzcmBpPmHPl6OzQ5cy1ur2YhzWsCBzWAm7EutFzBmMm-aKmum6eHJI8h_A0WxkqyEWu0X9MJ81lWcrREvtIcoslQ0GWD5qxDKcABEpZ3Tlv9p9dTrVjhErzsMdByPuVZmH_S1PtqukYPmXAku6FOdm1pmSDNgecLHSP0AMh3HDJlfsWKkWt2y0j9KcndmKb8LuaH1H4A_od8n6eWW6aAwodU7hy1swS_jAAV73pPyt-DthXacfFiT6-OurNe2mQbZ_sI2Y4ltDT_vc7q0nbYcXGvi_OitTuffdLObUXLLIwPAE66FLIDVFabU3baHowvm7YzQ_fzd-sWO_ct7Ph85M7UF5q2-2YYA342pmhk4FoK7fxA0HlxDpZI5ojVFQ2ZomciRTjYRNaXUb721kZmikdzxKqn90OUMDQ9TGOH5bU83Ms07jPQnUfDjVvyrFCQPz_Naa7nrcGL19kOXc4MqVLTkVUz02uubxFaVbZSmCynSAXBcRhQujGIfeTZPRY7WxOaETHhWx3OTpPqMJpK23mK-4u_nib1IlqvbuB_CWXMD3thoTKc-9_YhB3muLndhsLJE3i2Ka9D3kx6pzkbGhHizbuwY3cQQhpSFbok28YCVXwddDzOH2KF-J5NKXVi0zCwAXY5EMyuV85Djg=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-24T13:25:00.000Z", "utc_arrival": "2023-06-24T11:25:00.000Z", "local_departure": "2023-06-24T10:05:00.000Z", "utc_departure": "2023-06-24T08:05:00.000Z"}, {"id": "0b770a224c32000091ac2e03_0|0a220b774c36000010c6991f_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 701.838113, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 210041.8887, "conversion": {"EUR": 549.838493, "HUF": 210041.8887}, "fare": {"adults": 105020.94, "children": 105020.94, "infants": 105020.94}, "bags_price": {"1": 68.992, "2": 137.984}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 3}, "airlines": ["FR"], "route": [{"id": "0b770a224c32000091ac2e03_0", "combination_id": "0b770a224c32000091ac2e03", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-29T14:00:00.000Z", "utc_arrival": "2023-05-29T12:00:00.000Z", "local_departure": "2023-05-29T10:40:00.000Z", "utc_departure": "2023-05-29T08:40:00.000Z"}, {"id": "0a220b774c36000010c6991f_0", "combination_id": "0a220b774c36000010c6991f", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-02T18:00:00.000Z", "utc_arrival": "2023-06-02T16:00:00.000Z", "local_departure": "2023-06-02T14:50:00.000Z", "utc_departure": "2023-06-02T12:50:00.000Z"}], "booking_token": "EtHMVOXbKByh-fxLJ_4MHWbWuD-n5jYuArhQib6zLcuFxd8wCHcgXozzt4tkUwp8as-sZmUiwOt_mdRZnyu4zVHtjirN5EgpSSrFlbaPpR48T_pEL7rPuPmh9LThELg6hNxaE0ZV_adnimfR_jSo2IshTLU-dL44uLm0D2SY_K6ePq4ISb_zdepBF-a7_fAr7JbAbpdFbqtPgdzRgeuGgwDBIvjHrItCJsejjNaLVaPit4t-6hNpRCAiLJM8JaZitPbEo5NM5iSdkb7Jp06GdM6U7tuUtFYJGu6kNEfW8k1jEHb4yZNZnbbBZgcGEsnKKwjD9rTK4YZ3nbAKapxonkTrHS_iYoJ1izjeN0pfQK3oyt1xeOp0n4BOd8bWSVpX0A04pSRkcI_sZD51rbuiKyI1UUqaHwbjpUQXjTrkJpUnKKSsHRMbqJ-jGmmj1CQUS6MtY-D3L2Y643W2Y9sp6KP_175pFtflpfDz8CExKEiVDm4NoVoBSLbFScuy0GgblccZappVylAizGDLP0kB7NH3V6CtTpjz5-D2BvryVVaulTE0tAQlrCpFTSRkGkOu6GVkVfSzcb-aaUxb1Jkb6QR2IgL4MK8ilbggplGmCxpDqrrMAnz81V85Oki9Ww21pTzjRJ5hjgQY8XHMZMpq4MBsSpYU3HUoGInbt1HQ8clh2xVvXdV1fVgIqSf1kMhww-meoubu3X-t6Acf2sM0b3525qhTRO71qPYm_p3DDKZILIzOY0tCTl7BNwOlJiR8ELF_Q5gNA2mmRO4IqT4ep3A==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c32000091ac2e03_0%7C0a220b774c36000010c6991f_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EtHMVOXbKByh-fxLJ_4MHWbWuD-n5jYuArhQib6zLcuFxd8wCHcgXozzt4tkUwp8as-sZmUiwOt_mdRZnyu4zVHtjirN5EgpSSrFlbaPpR48T_pEL7rPuPmh9LThELg6hNxaE0ZV_adnimfR_jSo2IshTLU-dL44uLm0D2SY_K6ePq4ISb_zdepBF-a7_fAr7JbAbpdFbqtPgdzRgeuGgwDBIvjHrItCJsejjNaLVaPit4t-6hNpRCAiLJM8JaZitPbEo5NM5iSdkb7Jp06GdM6U7tuUtFYJGu6kNEfW8k1jEHb4yZNZnbbBZgcGEsnKKwjD9rTK4YZ3nbAKapxonkTrHS_iYoJ1izjeN0pfQK3oyt1xeOp0n4BOd8bWSVpX0A04pSRkcI_sZD51rbuiKyI1UUqaHwbjpUQXjTrkJpUnKKSsHRMbqJ-jGmmj1CQUS6MtY-D3L2Y643W2Y9sp6KP_175pFtflpfDz8CExKEiVDm4NoVoBSLbFScuy0GgblccZappVylAizGDLP0kB7NH3V6CtTpjz5-D2BvryVVaulTE0tAQlrCpFTSRkGkOu6GVkVfSzcb-aaUxb1Jkb6QR2IgL4MK8ilbggplGmCxpDqrrMAnz81V85Oki9Ww21pTzjRJ5hjgQY8XHMZMpq4MBsSpYU3HUoGInbt1HQ8clh2xVvXdV1fVgIqSf1kMhww-meoubu3X-t6Acf2sM0b3525qhTRO71qPYm_p3DDKZILIzOY0tCTl7BNwOlJiR8ELF_Q5gNA2mmRO4IqT4ep3A==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-29T14:00:00.000Z", "utc_arrival": "2023-05-29T12:00:00.000Z", "local_departure": "2023-05-29T10:40:00.000Z", "utc_departure": "2023-05-29T08:40:00.000Z"}, {"id": "0b770a224c440000087d9250_0|0a220b774c48000056e1c9c9_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 703.811766, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 210795.837, "conversion": {"EUR": 551.812146, "HUF": 210795.837}, "fare": {"adults": 105397.92, "children": 105397.92, "infants": 105397.92}, "bags_price": {"1": 80.682, "2": 171.15}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 158, "hold_height": 52, "hold_length": 78, "hold_weight": 20, "hold_width": 28, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 3, "personal_item_width": 15}, "availability": {"seats": 3}, "airlines": ["FR", "IB"], "route": [{"id": "0b770a224c440000087d9250_0", "combination_id": "0b770a224c440000087d9250", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-16T21:45:00.000Z", "utc_arrival": "2023-06-16T19:45:00.000Z", "local_departure": "2023-06-16T18:25:00.000Z", "utc_departure": "2023-06-16T16:25:00.000Z"}, {"id": "0a220b774c48000056e1c9c9_0", "combination_id": "0a220b774c48000056e1c9c9", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "IB", "flight_no": 3278, "operating_carrier": "IB", "operating_flight_no": "3278", "fare_basis": "QDNNAOB4", "fare_category": "M", "fare_classes": "Q", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-20T14:55:00.000Z", "utc_arrival": "2023-06-20T12:55:00.000Z", "local_departure": "2023-06-20T11:45:00.000Z", "utc_departure": "2023-06-20T09:45:00.000Z"}], "booking_token": "EB_T0xtoO0_FQVZib4iRG7HOesmiO3itEYu2sz802IH53C6u4HKozMrPokL2bRkzNjKYlunKnJBwrUMCLpseHQxjtOtPGP1wrABz7DN8BJsp_jRDBOIyPFpQz1wSvWj9jAU0O9warQxyfDRgtQHzWkAI9q5dcqhlYh_sShjpX6N1Tl1yKs3nE0CkNklOFnpn4ZNj8_Pwv73mpnnConkGAvCeUdhjbBoFRhCTex4VdnhTdAt9CF9Ymr4NK5IblgiDQIVfTMPOFXSZVUFHQ9FeW-3SrwKpa9Z4ErCT-3_4IaovI2EdEIjeTaFinm5vM41eWo0zgWQLLcHetiAXeZ3wmERfSZFk2JUvMu1yLAuArUPIXHRV6KE40O6I_kXR9GczkUgSUmZHopmB4mUXMKNAF6CujiUbU_zxCB2QzAOWlJEJ21vEpq2RnuK7qI8l-K7czFW7VTjgLxxUk0D3II89fb1d7MghVK-nd2OHDNInpg71iCPQS0aHsJFoDw1OQ2gDI_ATVjX5G8Mtq8OYiqPRlulDvQvEV2VlgeK8N_vWF2Kl_N5j3McdD8E1huJtHzWYLSnvhQAdXs5Xgu-gRRTXPVvOT1MBceO1KU3RbZHGP8iGzISJ4VbKNJkvn_ZUhn2uMV0xzbWhx_O-hD8USZXcxlSsoNA-3Cj9AGV0RerV4QrRr4kQ5p22qnXCLGayetgJSkU_J6B1h2NO9wtKLOWNwsZ-5-IYrwomMw_H0XKPFDmqsoo3Dz7QbdwOzprrOgXzNuNuq9hsV3Q1ad-ufUi94aujNbYfqc6dVv9yFPjZsK89sRMw6GK9J99ZOHD5KPkPF", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c440000087d9250_0%7C0a220b774c48000056e1c9c9_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EB_T0xtoO0_FQVZib4iRG7HOesmiO3itEYu2sz802IH53C6u4HKozMrPokL2bRkzNjKYlunKnJBwrUMCLpseHQxjtOtPGP1wrABz7DN8BJsp_jRDBOIyPFpQz1wSvWj9jAU0O9warQxyfDRgtQHzWkAI9q5dcqhlYh_sShjpX6N1Tl1yKs3nE0CkNklOFnpn4ZNj8_Pwv73mpnnConkGAvCeUdhjbBoFRhCTex4VdnhTdAt9CF9Ymr4NK5IblgiDQIVfTMPOFXSZVUFHQ9FeW-3SrwKpa9Z4ErCT-3_4IaovI2EdEIjeTaFinm5vM41eWo0zgWQLLcHetiAXeZ3wmERfSZFk2JUvMu1yLAuArUPIXHRV6KE40O6I_kXR9GczkUgSUmZHopmB4mUXMKNAF6CujiUbU_zxCB2QzAOWlJEJ21vEpq2RnuK7qI8l-K7czFW7VTjgLxxUk0D3II89fb1d7MghVK-nd2OHDNInpg71iCPQS0aHsJFoDw1OQ2gDI_ATVjX5G8Mtq8OYiqPRlulDvQvEV2VlgeK8N_vWF2Kl_N5j3McdD8E1huJtHzWYLSnvhQAdXs5Xgu-gRRTXPVvOT1MBceO1KU3RbZHGP8iGzISJ4VbKNJkvn_ZUhn2uMV0xzbWhx_O-hD8USZXcxlSsoNA-3Cj9AGV0RerV4QrRr4kQ5p22qnXCLGayetgJSkU_J6B1h2NO9wtKLOWNwsZ-5-IYrwomMw_H0XKPFDmqsoo3Dz7QbdwOzprrOgXzNuNuq9hsV3Q1ad-ufUi94aujNbYfqc6dVv9yFPjZsK89sRMw6GK9J99ZOHD5KPkPF", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-16T21:45:00.000Z", "utc_arrival": "2023-06-16T19:45:00.000Z", "local_departure": "2023-06-16T18:25:00.000Z", "utc_departure": "2023-06-16T16:25:00.000Z"}, {"id": "0b770a224c3d0000866dbf36_0|0a220b774c4100004abd18f4_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 709.397435, "distance": 1975.87, "duration": {"departure": 12600, "return": 11400, "total": 24000}, "price": 211910.9175, "conversion": {"EUR": 554.731155, "HUF": 211910.9175}, "fare": {"adults": 105955.46, "children": 105955.46, "infants": 105955.46}, "bags_price": {"1": 98.7, "2": 207.2}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 158, "hold_height": 52, "hold_length": 78, "hold_weight": 20, "hold_width": 28, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 3, "personal_item_width": 15}, "availability": {"seats": 3}, "airlines": ["W6", "IB"], "route": [{"id": "0b770a224c3d0000866dbf36_0", "combination_id": "0b770a224c3d0000866dbf36", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "KREG", "fare_category": "M", "fare_classes": "K", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-09T20:45:00.000Z", "utc_arrival": "2023-06-09T18:45:00.000Z", "local_departure": "2023-06-09T17:15:00.000Z", "utc_departure": "2023-06-09T15:15:00.000Z"}, {"id": "0a220b774c4100004abd18f4_0", "combination_id": "0a220b774c4100004abd18f4", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "IB", "flight_no": 3278, "operating_carrier": "IB", "operating_flight_no": "3278", "fare_basis": "NWNNAOB4", "fare_category": "M", "fare_classes": "N", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-13T14:55:00.000Z", "utc_arrival": "2023-06-13T12:55:00.000Z", "local_departure": "2023-06-13T11:45:00.000Z", "utc_departure": "2023-06-13T09:45:00.000Z"}], "booking_token": "ElT8dwxKsiSaAAWVolnv6KFBgnvA4LYTUjeS5n1gx_NcemyL3nGg9awEImHO61ZZHy6nyNVsSp7emDNwCFvpNF-BBY-rvb98mxTuZgEvOLqqOBbrli5JIokELceZwF2YfNcPf1Mnly4Wuob6dfLcQUUrId_jL69yaOLnVv6FQ97qxfR55o3_lM5m_e8lKnadSYL2yJJF7qg0VdxxRPkNIJPZExjXH9B4qbejq9SqwfXx5Lrpm9IUjQePtcMCcnMbTiF3t06LZ7sP0ZgkYkQRNUHd9RipEe5Mh3_f_-6xZkY60BY-k5BfTBmpiMRxQAYDx51MOsi8zb_dUykbFnnjvu2okxriIjBB9WVsBXNBbww4wpJ0wgEdLeGvYbv5fNgp6R_zTz_W_DGdVzzjFBYEHnfQkIGda3AY5HU0__mugBukjkKiTE4_k-l2OppVb05tETMMXN_bC0n-ePJgRe8aBfFGp1g_N-B1ipi2E0QLexrZoevtl373d-1qGQ7YPHA2o53mLT1gOPo70-6yCeCq33on0wR74czv97afzIScOWt5LgC-flOtExaFJpxOReIPH9BNhfCnPxQXtHoi-KRSTkXc0XhFyKdyZOrIWOgxo7NnY410usurPc3XZUJyj9sBftGEGy1ieYqDG3zzjS_rw6fkWRJjHQeLz156qsoBMLQjVoVBAiwC_6b1UC_LcBMN0G8pOuJ89kzo6IVi6GajqBoc23_7-dD3VMMB0HnTRAIjPMx40SMoq3BNlTkek0TzjM_M8aWnnuFZveALzmZfu17bBY-3xb__u2unNrjZ0Uq0=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c3d0000866dbf36_0%7C0a220b774c4100004abd18f4_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=ElT8dwxKsiSaAAWVolnv6KFBgnvA4LYTUjeS5n1gx_NcemyL3nGg9awEImHO61ZZHy6nyNVsSp7emDNwCFvpNF-BBY-rvb98mxTuZgEvOLqqOBbrli5JIokELceZwF2YfNcPf1Mnly4Wuob6dfLcQUUrId_jL69yaOLnVv6FQ97qxfR55o3_lM5m_e8lKnadSYL2yJJF7qg0VdxxRPkNIJPZExjXH9B4qbejq9SqwfXx5Lrpm9IUjQePtcMCcnMbTiF3t06LZ7sP0ZgkYkQRNUHd9RipEe5Mh3_f_-6xZkY60BY-k5BfTBmpiMRxQAYDx51MOsi8zb_dUykbFnnjvu2okxriIjBB9WVsBXNBbww4wpJ0wgEdLeGvYbv5fNgp6R_zTz_W_DGdVzzjFBYEHnfQkIGda3AY5HU0__mugBukjkKiTE4_k-l2OppVb05tETMMXN_bC0n-ePJgRe8aBfFGp1g_N-B1ipi2E0QLexrZoevtl373d-1qGQ7YPHA2o53mLT1gOPo70-6yCeCq33on0wR74czv97afzIScOWt5LgC-flOtExaFJpxOReIPH9BNhfCnPxQXtHoi-KRSTkXc0XhFyKdyZOrIWOgxo7NnY410usurPc3XZUJyj9sBftGEGy1ieYqDG3zzjS_rw6fkWRJjHQeLz156qsoBMLQjVoVBAiwC_6b1UC_LcBMN0G8pOuJ89kzo6IVi6GajqBoc23_7-dD3VMMB0HnTRAIjPMx40SMoq3BNlTkek0TzjM_M8aWnnuFZveALzmZfu17bBY-3xb__u2unNrjZ0Uq0=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-09T20:45:00.000Z", "utc_arrival": "2023-06-09T18:45:00.000Z", "local_departure": "2023-06-09T17:15:00.000Z", "utc_departure": "2023-06-09T15:15:00.000Z"}, {"id": "0b770a224c4b000059b2d558_0|0a220b774c4e0000de14d559_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 708.925644, "distance": 1975.87, "duration": {"departure": 12000, "return": 11700, "total": 23700}, "price": 212240.031, "conversion": {"EUR": 555.592694, "HUF": 212240.031}, "fare": {"adults": 106120.02, "children": 109425.32, "infants": 109425.32}, "bags_price": {"1": 97.93, "2": 195.86}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 3}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224c4b000059b2d558_0", "combination_id": "0b770a224c4b000059b2d558", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-23T21:45:00.000Z", "utc_arrival": "2023-06-23T19:45:00.000Z", "local_departure": "2023-06-23T18:25:00.000Z", "utc_departure": "2023-06-23T16:25:00.000Z"}, {"id": "0a220b774c4e0000de14d559_0", "combination_id": "0a220b774c4e0000de14d559", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IJREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-26T23:45:00.000Z", "utc_arrival": "2023-06-26T21:45:00.000Z", "local_departure": "2023-06-26T20:30:00.000Z", "utc_departure": "2023-06-26T18:30:00.000Z"}], "booking_token": "EgnG4CNFQ9Yqu5fyoGqT4hBz8TrNJGpaI0irSYgz5FM-kaCGvJT-QWzlfsnPn3Ad4azBaE5_ovSI-tZFP6WjQbNiWRrhj5thyx-flvltgnHZcGy1fDGGD4CTg1qm8xECD-cuWZFcRZ2zlrONQXrQPIQmI2AW1vzc6E62PY8IZ0fYuT0yjnrG78ba41V6O9Y27OiEAOFwa9cyDzmlO8jzWbDKAw6G3y7u8tXbwFuhqD-rsbwpWLtniYExBqwe9VpdCnUqWntbvfKEzVupAg5QTSJNH3lOIw5VJccKWQ6EyEDMbXnXucAc3XcCuv1aml9ILtN35qkmzNuaP-g0ZHfaWL-yV74U7sExjLkhdFFseW52iwyoQ8pyNwqScpQas3pXBH66rUr6NfRhwy6ikuMjz7NrbG5fq-ASUJXlNY5U2EqkpqxWaTfscO6n3PzDOyAEwUcDF4oInpFVMguR-NTnqev-sWNwKi-wb2f5iaZZsSRELZtDiQsKrA2Cc8Coja6fvQS4pANgk0Wf1G9fwIwRF9l5jU-GGgjs8H1hAJRaTX7j4_OdfqnO13siLeKJgvZs5bBHnRNIY7au4T2J_oAsfbVxy9OegLNOwf7gAFu5eQo-pclHqgKewGSyhMIX_0G5rDKPscEt3Q5KTWhI1Fj5qhgKZZ6c3nMNknk7aZ_bb1GIXKpbzz7r2RwSFVJsReDrbtdBPNmid6fjVmgFfJMFEJray6yWeL8MJljaN-Bwv6JciAgfJNxkfqONxIZwxwZxZUrPbidqtmg5S_WjLVc8Ag7yY1hMP4e_WrGT2fLxzB2E=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c4b000059b2d558_0%7C0a220b774c4e0000de14d559_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EgnG4CNFQ9Yqu5fyoGqT4hBz8TrNJGpaI0irSYgz5FM-kaCGvJT-QWzlfsnPn3Ad4azBaE5_ovSI-tZFP6WjQbNiWRrhj5thyx-flvltgnHZcGy1fDGGD4CTg1qm8xECD-cuWZFcRZ2zlrONQXrQPIQmI2AW1vzc6E62PY8IZ0fYuT0yjnrG78ba41V6O9Y27OiEAOFwa9cyDzmlO8jzWbDKAw6G3y7u8tXbwFuhqD-rsbwpWLtniYExBqwe9VpdCnUqWntbvfKEzVupAg5QTSJNH3lOIw5VJccKWQ6EyEDMbXnXucAc3XcCuv1aml9ILtN35qkmzNuaP-g0ZHfaWL-yV74U7sExjLkhdFFseW52iwyoQ8pyNwqScpQas3pXBH66rUr6NfRhwy6ikuMjz7NrbG5fq-ASUJXlNY5U2EqkpqxWaTfscO6n3PzDOyAEwUcDF4oInpFVMguR-NTnqev-sWNwKi-wb2f5iaZZsSRELZtDiQsKrA2Cc8Coja6fvQS4pANgk0Wf1G9fwIwRF9l5jU-GGgjs8H1hAJRaTX7j4_OdfqnO13siLeKJgvZs5bBHnRNIY7au4T2J_oAsfbVxy9OegLNOwf7gAFu5eQo-pclHqgKewGSyhMIX_0G5rDKPscEt3Q5KTWhI1Fj5qhgKZZ6c3nMNknk7aZ_bb1GIXKpbzz7r2RwSFVJsReDrbtdBPNmid6fjVmgFfJMFEJray6yWeL8MJljaN-Bwv6JciAgfJNxkfqONxIZwxwZxZUrPbidqtmg5S_WjLVc8Ag7yY1hMP4e_WrGT2fLxzB2E=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-23T21:45:00.000Z", "utc_arrival": "2023-06-23T19:45:00.000Z", "local_departure": "2023-06-23T18:25:00.000Z", "utc_departure": "2023-06-23T16:25:00.000Z"}, {"id": "0b770a224c1e00003e2ba34c_0|0a220b774c220000a4dc2bfb_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 708.450218, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 212567.7559, "conversion": {"EUR": 556.450598, "HUF": 212567.7559}, "fare": {"adults": 106283.88, "children": 110651.14, "infants": 110651.14}, "bags_price": {"1": 70.364, "2": 140.728}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 6}, "airlines": ["FR"], "route": [{"id": "0b770a224c1e00003e2ba34c_0", "combination_id": "0b770a224c1e00003e2ba34c", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-09T10:15:00.000Z", "utc_arrival": "2023-05-09T08:15:00.000Z", "local_departure": "2023-05-09T06:55:00.000Z", "utc_departure": "2023-05-09T04:55:00.000Z"}, {"id": "0a220b774c220000a4dc2bfb_0", "combination_id": "0a220b774c220000a4dc2bfb", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-13T09:40:00.000Z", "utc_arrival": "2023-05-13T07:40:00.000Z", "local_departure": "2023-05-13T06:30:00.000Z", "utc_departure": "2023-05-13T04:30:00.000Z"}], "booking_token": "EIkQSOYcjEMm3yV66igaRBu4aOupNSP10z1qCd2Vip41OITSJeGw8MpAWC_m1bPppTR7HJA6d6gjqWEQfGnIo856eomc6YawlaY6PFGK2ay51lLIOisvGbI8NNoQ-tQcDz1LSGJyzBhudQfue1MXBhYRg78j78CiciU-BPJ42vzDgI1xRdnv38pIc7XOYXRZuCDEuYRE1Y0dpF5DzXugNzjqbcJ6KluArumbJ1HILSlt3b8uijH7nDAfIuPNGHFZGWI5fq6kMYdIuDQYwVoPutFjk6jm8OT8j-NDkH39jdaFoLMdZMsIadf6YJu9jwe_f_ERn0yE8_it_dLN2d2kAI-3jxrFjAUDTve7ICdo5MtBNU4bcBgDDG87nW9LPUJqOrxFbFcjV7eVxISWQwyojrAD2MqnC6IW6s8_da_j7FHjx-q6P3xooPtnZxrlJW7BblKVM4PS5RmDWVqOv-ypB9pw0dbTTSOQpX0gLGuPN6a1ing8pJjFuU1lthXUX2_YNDG3jKmtr6hAJdjtnVqJTxq7GYdCwexsD4IZVfUFbl9ZfW8yc_KkVSiDa0_z_vcrRabVlYMWVAv2sRKMFwLiuG1Aq4wYF8VoHIhL7dhLHiJx9c5cjPDTfQ-bttKUAebtierg8rFDsp6f-cZX9rKpqNzVzaddVSDTikHoWX4HTQJbRDeE87dxnNjHBU_lKv9-NOMTJ9qim-jGSv6w53tpL8T27Ou9S9oHT_pv4_QDjyg1MENZpJohH51mFeEuUEVtA", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c1e00003e2ba34c_0%7C0a220b774c220000a4dc2bfb_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EIkQSOYcjEMm3yV66igaRBu4aOupNSP10z1qCd2Vip41OITSJeGw8MpAWC_m1bPppTR7HJA6d6gjqWEQfGnIo856eomc6YawlaY6PFGK2ay51lLIOisvGbI8NNoQ-tQcDz1LSGJyzBhudQfue1MXBhYRg78j78CiciU-BPJ42vzDgI1xRdnv38pIc7XOYXRZuCDEuYRE1Y0dpF5DzXugNzjqbcJ6KluArumbJ1HILSlt3b8uijH7nDAfIuPNGHFZGWI5fq6kMYdIuDQYwVoPutFjk6jm8OT8j-NDkH39jdaFoLMdZMsIadf6YJu9jwe_f_ERn0yE8_it_dLN2d2kAI-3jxrFjAUDTve7ICdo5MtBNU4bcBgDDG87nW9LPUJqOrxFbFcjV7eVxISWQwyojrAD2MqnC6IW6s8_da_j7FHjx-q6P3xooPtnZxrlJW7BblKVM4PS5RmDWVqOv-ypB9pw0dbTTSOQpX0gLGuPN6a1ing8pJjFuU1lthXUX2_YNDG3jKmtr6hAJdjtnVqJTxq7GYdCwexsD4IZVfUFbl9ZfW8yc_KkVSiDa0_z_vcrRabVlYMWVAv2sRKMFwLiuG1Aq4wYF8VoHIhL7dhLHiJx9c5cjPDTfQ-bttKUAebtierg8rFDsp6f-cZX9rKpqNzVzaddVSDTikHoWX4HTQJbRDeE87dxnNjHBU_lKv9-NOMTJ9qim-jGSv6w53tpL8T27Ou9S9oHT_pv4_QDjyg1MENZpJohH51mFeEuUEVtA", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-09T10:15:00.000Z", "utc_arrival": "2023-05-09T08:15:00.000Z", "local_departure": "2023-05-09T06:55:00.000Z", "utc_departure": "2023-05-09T04:55:00.000Z"}, {"id": "0b770a224c470000e38f46b1_0|0a220b774c4b0000d381db8e_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 710.166101, "distance": 1975.87, "duration": {"departure": 12000, "return": 11700, "total": 23700}, "price": 212713.8937, "conversion": {"EUR": 556.833151, "HUF": 212713.8937}, "fare": {"adults": 106356.95, "children": 106356.95, "infants": 106356.95}, "bags_price": {"1": 95.424, "2": 190.848}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 2}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224c470000e38f46b1_0", "combination_id": "0b770a224c470000e38f46b1", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-19T14:00:00.000Z", "utc_arrival": "2023-06-19T12:00:00.000Z", "local_departure": "2023-06-19T10:40:00.000Z", "utc_departure": "2023-06-19T08:40:00.000Z"}, {"id": "0a220b774c4b0000d381db8e_0", "combination_id": "0a220b774c4b0000d381db8e", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "JREG", "fare_category": "M", "fare_classes": "J", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-23T23:45:00.000Z", "utc_arrival": "2023-06-23T21:45:00.000Z", "local_departure": "2023-06-23T20:30:00.000Z", "utc_departure": "2023-06-23T18:30:00.000Z"}], "booking_token": "Enr7sP9xb0pPf0q9lkOoU4qD5hWFeinTFvSZW8S7SL0XNhl_tMtMWhExaO8kS4udlpVW-PiPOWCLZzc475c16Pm010uS2GO3XbdHA3tBjaMGWL4Z6y7LSY9S95rQpVXkVe6DZ4SgdKW9h9WxF0bWDAhNBZVnqJhr9Hi_uRA9uWVqtTx8HYe0h-2V46jcviIq6_tf_btxj9ZAm_ggnNuhoGCTDGzbfmveg4ex8mXvA30s9phYWeo7AH_3pu0B0cFHPVKV7P_eAYLOG4J3vWVHU_fmQNRLwC7atrlHfN-EJg_3lD6LfqVkIMIMNS0p1Uv4GzxC-UaAOHsmSJZIpCWFQPRL6l_yyEfPP-JHA7rj2aPOWOGc7InWey9nJJ5QFw-k3UCSmCTIVL3w1XMIRtE01jdYz6-PJVJsIp7w9ftROzlLqAJPwQQlincdHRgNTVo_B8v2ELN8OkScxr3g1NV9kSFz8I4E6X2fbjCLBckS9EBeZhDC5qexK9TMvtWRA22FTTeHvmMgTyCyQ_VrOIYDipGpZdJ62VMb7uyRUbi5K0P9MEx7tv8vhZ9VPoM9YmYLLjl3T1rVUI8JrfTur7cwbiNmKD0-Pgs-4CmMgZaGZtxGRFuke9kTJASX-aPcwAeabE1W6N8sb45bJH8ElvfNX4DMsXV8NReYu5tgau-ii_MOy6kVqgrtDK_UKLzOM-lxONhsuqTtIRrMvKDhA3-bQYFzMxTHDLVJJd2c9CFgAi2WwfhIOZz_d6OzNgLrBIR2tg8qTlIZquom8VYxl1UlWPQ==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c470000e38f46b1_0%7C0a220b774c4b0000d381db8e_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=Enr7sP9xb0pPf0q9lkOoU4qD5hWFeinTFvSZW8S7SL0XNhl_tMtMWhExaO8kS4udlpVW-PiPOWCLZzc475c16Pm010uS2GO3XbdHA3tBjaMGWL4Z6y7LSY9S95rQpVXkVe6DZ4SgdKW9h9WxF0bWDAhNBZVnqJhr9Hi_uRA9uWVqtTx8HYe0h-2V46jcviIq6_tf_btxj9ZAm_ggnNuhoGCTDGzbfmveg4ex8mXvA30s9phYWeo7AH_3pu0B0cFHPVKV7P_eAYLOG4J3vWVHU_fmQNRLwC7atrlHfN-EJg_3lD6LfqVkIMIMNS0p1Uv4GzxC-UaAOHsmSJZIpCWFQPRL6l_yyEfPP-JHA7rj2aPOWOGc7InWey9nJJ5QFw-k3UCSmCTIVL3w1XMIRtE01jdYz6-PJVJsIp7w9ftROzlLqAJPwQQlincdHRgNTVo_B8v2ELN8OkScxr3g1NV9kSFz8I4E6X2fbjCLBckS9EBeZhDC5qexK9TMvtWRA22FTTeHvmMgTyCyQ_VrOIYDipGpZdJ62VMb7uyRUbi5K0P9MEx7tv8vhZ9VPoM9YmYLLjl3T1rVUI8JrfTur7cwbiNmKD0-Pgs-4CmMgZaGZtxGRFuke9kTJASX-aPcwAeabE1W6N8sb45bJH8ElvfNX4DMsXV8NReYu5tgau-ii_MOy6kVqgrtDK_UKLzOM-lxONhsuqTtIRrMvKDhA3-bQYFzMxTHDLVJJd2c9CFgAi2WwfhIOZz_d6OzNgLrBIR2tg8qTlIZquom8VYxl1UlWPQ==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-19T14:00:00.000Z", "utc_arrival": "2023-06-19T12:00:00.000Z", "local_departure": "2023-06-19T10:40:00.000Z", "utc_departure": "2023-06-19T08:40:00.000Z"}, {"id": "0b770a224c470000e38f46b1_0|0a220b774c4a0000f5177ada_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 710.166101, "distance": 1975.87, "duration": {"departure": 12000, "return": 11700, "total": 23700}, "price": 212713.8937, "conversion": {"EUR": 556.833151, "HUF": 212713.8937}, "fare": {"adults": 106356.95, "children": 106356.95, "infants": 106356.95}, "bags_price": {"1": 95.424, "2": 190.848}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 4}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224c470000e38f46b1_0", "combination_id": "0b770a224c470000e38f46b1", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-19T14:00:00.000Z", "utc_arrival": "2023-06-19T12:00:00.000Z", "local_departure": "2023-06-19T10:40:00.000Z", "utc_departure": "2023-06-19T08:40:00.000Z"}, {"id": "0a220b774c4a0000f5177ada_0", "combination_id": "0a220b774c4a0000f5177ada", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "JREG", "fare_category": "M", "fare_classes": "J", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-23T01:15:00.000Z", "utc_arrival": "2023-06-22T23:15:00.000Z", "local_departure": "2023-06-22T22:00:00.000Z", "utc_departure": "2023-06-22T20:00:00.000Z"}], "booking_token": "ELk_pQNeC6zZ1rqqkMyC9khi-TZ60tB9ILOidHJfBH2PTsXKE-E1GaeLJ22clDIWVHKxK0sU1Mz_YdcNCaz6VRRhIk5hdwIMRKWctdnJPMiGLo1LBHMkVsRrg9H8oNSUeVTr8bKS84He5faunCqoTgbhnaE1dSHaVMZDPFxsN-YWdaDI5sZZXdOHBaHE53_-x-zQnZdfjat-ToFbk3wxWykBkmIONH8yb1Zv99G8omqUJt9piDK6JdF7PEH1WZ-B8r5GzV85qSvDXEEtFRvHLdIbz4mMRTaa0dHOHeiw2pArL5jY6BSra-8057h6yLEEf2Rl94RVVJ9tM6RipNJaOgQ9os4-I5dEiVQOUHYyGMwLHnwbMBWendwgC8XUwIb-vD2PmNkXOLvbNMcNXkKfAD8wu45eDSxacw2efHIKf7v2ERixm-fueDz1hC4faK5QFKxcOea0hbmCdzDGLVPxMVy8OYXMsZV2eAr5SS1sUyxHV_R5C6Yx9rTr78z0wC9TG4iSa3gaIedURUVD8XBjc9I3rgXUlXsjz4WgopGgL-jbRnghtnD5vhAEoi03utvo-FTkmZs4XcTTiXl8llWOQLJiA7N9F_5BV_Oaoy-fCGS01LefAr_lTar5ewl0x2iUYztmHVi-nY5MJsxq3-vYIC7SHnZu_HoYBZ1faEokfXM-xTdHGyW2_nL1sGCdaul_XLYR04-hvAOAzA8cssAoydastBPcRCSSu0MfUtioPnwm67Bxd0ypCDngxp505JJGX", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c470000e38f46b1_0%7C0a220b774c4a0000f5177ada_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=ELk_pQNeC6zZ1rqqkMyC9khi-TZ60tB9ILOidHJfBH2PTsXKE-E1GaeLJ22clDIWVHKxK0sU1Mz_YdcNCaz6VRRhIk5hdwIMRKWctdnJPMiGLo1LBHMkVsRrg9H8oNSUeVTr8bKS84He5faunCqoTgbhnaE1dSHaVMZDPFxsN-YWdaDI5sZZXdOHBaHE53_-x-zQnZdfjat-ToFbk3wxWykBkmIONH8yb1Zv99G8omqUJt9piDK6JdF7PEH1WZ-B8r5GzV85qSvDXEEtFRvHLdIbz4mMRTaa0dHOHeiw2pArL5jY6BSra-8057h6yLEEf2Rl94RVVJ9tM6RipNJaOgQ9os4-I5dEiVQOUHYyGMwLHnwbMBWendwgC8XUwIb-vD2PmNkXOLvbNMcNXkKfAD8wu45eDSxacw2efHIKf7v2ERixm-fueDz1hC4faK5QFKxcOea0hbmCdzDGLVPxMVy8OYXMsZV2eAr5SS1sUyxHV_R5C6Yx9rTr78z0wC9TG4iSa3gaIedURUVD8XBjc9I3rgXUlXsjz4WgopGgL-jbRnghtnD5vhAEoi03utvo-FTkmZs4XcTTiXl8llWOQLJiA7N9F_5BV_Oaoy-fCGS01LefAr_lTar5ewl0x2iUYztmHVi-nY5MJsxq3-vYIC7SHnZu_HoYBZ1faEokfXM-xTdHGyW2_nL1sGCdaul_XLYR04-hvAOAzA8cssAoydastBPcRCSSu0MfUtioPnwm67Bxd0ypCDngxp505JJGX", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-19T14:00:00.000Z", "utc_arrival": "2023-06-19T12:00:00.000Z", "local_departure": "2023-06-19T10:40:00.000Z", "utc_departure": "2023-06-19T08:40:00.000Z"}, {"id": "0b770a224c2a00009d1d2148_0|0a220b774c2e0000ad0adba8_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 713.894513, "distance": 1975.87, "duration": {"departure": 12600, "return": 11700, "total": 24300}, "price": 213119.4899, "conversion": {"EUR": 557.894903, "HUF": 213119.4899}, "fare": {"adults": 106559.74, "children": 109961.17, "infants": 109961.17}, "bags_price": {"1": 83.146, "2": 166.278}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 439, "hold_height": 149, "hold_length": 171, "hold_weight": 20, "hold_width": 119, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 6}, "airlines": ["W6"], "route": [{"id": "0b770a224c2a00009d1d2148_0", "combination_id": "0b770a224c2a00009d1d2148", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IJREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-21T17:05:00.000Z", "utc_arrival": "2023-05-21T15:05:00.000Z", "local_departure": "2023-05-21T13:35:00.000Z", "utc_departure": "2023-05-21T11:35:00.000Z"}, {"id": "0a220b774c2e0000ad0adba8_0", "combination_id": "0a220b774c2e0000ad0adba8", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IJREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-26T01:15:00.000Z", "utc_arrival": "2023-05-25T23:15:00.000Z", "local_departure": "2023-05-25T22:00:00.000Z", "utc_departure": "2023-05-25T20:00:00.000Z"}], "booking_token": "EweiwmCWcwTlFqOaTszYfckUYVzsCCHXPMqS5MRUiU6p1W9pI2RFNESssMPAo09kJGyBgLiZev_bwB_DMV5kmOWQ7mjXpODBqtNaxIL2Hr8rf_zcFx7V-dnJhQ0AAnGVniLlMjW-0WKEU-n0GmWOf9YorR5ij2btD0UbSfziDWEKMBo5rr79RTi0jCqIYTeJfjmpkwtKSGARQXTKbGRHPudnIeRah1xyKaotofjhKrD1jD8g4hzbgeoG42Tf1UZx8wL_fDNyPcr4jMRsCB9c0eZ_qj2vlbYMoKVyDp-EEG6mdxpZgJ64WCEPvSvGpJJu5-etQB1nieJFUP-83C6B2yFxYf86dtZtOLf7x9vufjZjr_U3NGtWyhJlBI1h4kOa_M0Me7-O4Kbb5ljqhSueJuTTEG61cAIL3Uza5UyBe0Fb0iaucVxjup4H4RKAPgQWuHTWfff6UFQuNr1CEoyYfSVfroqdTrtXZlz2aRzmWHpLbTQcHCmIAeopVCfRZmXx-pcYUR1H9dDLPQSKdFh39A8-xz7g4l7zptkGsALpICUlT-5sWdcB2rZ8MDlEBjlnhZd6wjBUamX0UzgEtd7oLFUx8kwtMDARdDTCsqegQCoBSZZj6A9anpoXcu1vaJzxFtEbMtphQbBDHkExcQyBK4UDt-9YcEzQI49trinUD6_XD60ztgBG__RPR0MDxst3yF-j86Th7tVBIw8ozIz0lDEmuHUigzz0aRAkaUWhlNbUr8F1xtMI3NM7d3yWleN1HUxp2_3rzyKuzq9g_hn8MCFTUCekxU7D0WlD2Wj3BRDs=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c2a00009d1d2148_0%7C0a220b774c2e0000ad0adba8_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EweiwmCWcwTlFqOaTszYfckUYVzsCCHXPMqS5MRUiU6p1W9pI2RFNESssMPAo09kJGyBgLiZev_bwB_DMV5kmOWQ7mjXpODBqtNaxIL2Hr8rf_zcFx7V-dnJhQ0AAnGVniLlMjW-0WKEU-n0GmWOf9YorR5ij2btD0UbSfziDWEKMBo5rr79RTi0jCqIYTeJfjmpkwtKSGARQXTKbGRHPudnIeRah1xyKaotofjhKrD1jD8g4hzbgeoG42Tf1UZx8wL_fDNyPcr4jMRsCB9c0eZ_qj2vlbYMoKVyDp-EEG6mdxpZgJ64WCEPvSvGpJJu5-etQB1nieJFUP-83C6B2yFxYf86dtZtOLf7x9vufjZjr_U3NGtWyhJlBI1h4kOa_M0Me7-O4Kbb5ljqhSueJuTTEG61cAIL3Uza5UyBe0Fb0iaucVxjup4H4RKAPgQWuHTWfff6UFQuNr1CEoyYfSVfroqdTrtXZlz2aRzmWHpLbTQcHCmIAeopVCfRZmXx-pcYUR1H9dDLPQSKdFh39A8-xz7g4l7zptkGsALpICUlT-5sWdcB2rZ8MDlEBjlnhZd6wjBUamX0UzgEtd7oLFUx8kwtMDARdDTCsqegQCoBSZZj6A9anpoXcu1vaJzxFtEbMtphQbBDHkExcQyBK4UDt-9YcEzQI49trinUD6_XD60ztgBG__RPR0MDxst3yF-j86Th7tVBIw8ozIz0lDEmuHUigzz0aRAkaUWhlNbUr8F1xtMI3NM7d3yWleN1HUxp2_3rzyKuzq9g_hn8MCFTUCekxU7D0WlD2Wj3BRDs=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-21T17:05:00.000Z", "utc_arrival": "2023-05-21T15:05:00.000Z", "local_departure": "2023-05-21T13:35:00.000Z", "utc_departure": "2023-05-21T11:35:00.000Z"}, {"id": "0b770a224c040000025fb1e5_0|0a220b774c080000c0858f1c_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 715.990077, "distance": 1975.87, "duration": {"departure": 12600, "return": 11700, "total": 24300}, "price": 213920.009, "conversion": {"EUR": 559.990467, "HUF": 213920.009}, "fare": {"adults": 106960, "children": 106960, "infants": 106960}, "bags_price": {"1": 134.344, "2": 268.66}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 439, "hold_height": 149, "hold_length": 171, "hold_weight": 20, "hold_width": 119, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 2}, "airlines": ["W6"], "route": [{"id": "0b770a224c040000025fb1e5_0", "combination_id": "0b770a224c040000025fb1e5", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-13T21:15:00.000Z", "utc_arrival": "2023-04-13T19:15:00.000Z", "local_departure": "2023-04-13T17:45:00.000Z", "utc_departure": "2023-04-13T15:45:00.000Z"}, {"id": "0a220b774c080000c0858f1c_0", "combination_id": "0a220b774c080000c0858f1c", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "BREG", "fare_category": "M", "fare_classes": "B", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-17T23:45:00.000Z", "utc_arrival": "2023-04-17T21:45:00.000Z", "local_departure": "2023-04-17T20:30:00.000Z", "utc_departure": "2023-04-17T18:30:00.000Z"}], "booking_token": "EeovJEOu1-LKt-_c28GsWl89GMPIOfANv3jEN820ntbqjcwi4_-3Q9o-8Z5rMkeUFbH5xCyF1B-yFnxwHxz2tZmXvMgK_RIvumYPmFbv2vv_FQ_VaM6AzQE66plnMQeO96ICbXz3njh_iEPOcDEO_F8Tru-nDeVNZ1Fpekfx9dyPlOv-fcf69xtRby1nHk8Upteuh9SyQpi3g2o7j8-05ycaQBqPADwyBQhmNxXOsRd0sjN1dcZFZVXLnkG0EuJnSQqsfzyytbXu_bms1TOqSobXWPtXwoGY9yiiPz9dJO59UnVu70qy5buZbXje9JeQKpH0uakxQFeiXDiJhMd-XZ1fB887ZriVoHuxOMafveQEX4BvgRILcabB2Xq1N6r2dX1UYPfAhbhp6NCdjdfM1Yh_Gzzry3M-2Fv8MMFd0o6brYa-cqnwF68Q3cvDv-zcU1m2JasLe_Kk2CtsXJEvtA-lP33PSzA0WZoIKRyliem4dGkMOci-jgkDlBNDTgVID7m8UgFdcDdBcopF1IrB8s3l9sFgQxZxguFG-hnx5d1OrSYQg5I9jMbM9DTkdFsKoz3k4bac3zCkEQYlu2jxKua7AOWWFvLlncmkdHhniRwK2BS_wdX7JkWLv9pW4E7xxLeXnToo2ENds76tUBUOewxk0Agpew2NN9fQ_R1Uoq11RPjBB6yYKRL8Blk4uNFPOc0LxH9pe5qYVNSEBp2tJdCMLcUDnuTmt_jSN-qyYYG3c-5aS8eve9Rj3ymLHOwpExyerNM6P6N7uKsXqh4a-pGrkW_wyOl_aaEdHmKfYP_E=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c040000025fb1e5_0%7C0a220b774c080000c0858f1c_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EeovJEOu1-LKt-_c28GsWl89GMPIOfANv3jEN820ntbqjcwi4_-3Q9o-8Z5rMkeUFbH5xCyF1B-yFnxwHxz2tZmXvMgK_RIvumYPmFbv2vv_FQ_VaM6AzQE66plnMQeO96ICbXz3njh_iEPOcDEO_F8Tru-nDeVNZ1Fpekfx9dyPlOv-fcf69xtRby1nHk8Upteuh9SyQpi3g2o7j8-05ycaQBqPADwyBQhmNxXOsRd0sjN1dcZFZVXLnkG0EuJnSQqsfzyytbXu_bms1TOqSobXWPtXwoGY9yiiPz9dJO59UnVu70qy5buZbXje9JeQKpH0uakxQFeiXDiJhMd-XZ1fB887ZriVoHuxOMafveQEX4BvgRILcabB2Xq1N6r2dX1UYPfAhbhp6NCdjdfM1Yh_Gzzry3M-2Fv8MMFd0o6brYa-cqnwF68Q3cvDv-zcU1m2JasLe_Kk2CtsXJEvtA-lP33PSzA0WZoIKRyliem4dGkMOci-jgkDlBNDTgVID7m8UgFdcDdBcopF1IrB8s3l9sFgQxZxguFG-hnx5d1OrSYQg5I9jMbM9DTkdFsKoz3k4bac3zCkEQYlu2jxKua7AOWWFvLlncmkdHhniRwK2BS_wdX7JkWLv9pW4E7xxLeXnToo2ENds76tUBUOewxk0Agpew2NN9fQ_R1Uoq11RPjBB6yYKRL8Blk4uNFPOc0LxH9pe5qYVNSEBp2tJdCMLcUDnuTmt_jSN-qyYYG3c-5aS8eve9Rj3ymLHOwpExyerNM6P6N7uKsXqh4a-pGrkW_wyOl_aaEdHmKfYP_E=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-04-13T21:15:00.000Z", "utc_arrival": "2023-04-13T19:15:00.000Z", "local_departure": "2023-04-13T17:45:00.000Z", "utc_departure": "2023-04-13T15:45:00.000Z"}, {"id": "0b770a224c0d0000b8e97468_0|0a220b774c10000085c9a6d8_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 712.487584, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 214110.0561, "conversion": {"EUR": 560.487964, "HUF": 214110.0561}, "fare": {"adults": 107055.03, "children": 107055.03, "infants": 107055.03}, "bags_price": {"1": 91.98, "2": 183.96}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 5}, "airlines": ["FR"], "route": [{"id": "0b770a224c0d0000b8e97468_0", "combination_id": "0b770a224c0d0000b8e97468", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-22T13:25:00.000Z", "utc_arrival": "2023-04-22T11:25:00.000Z", "local_departure": "2023-04-22T10:05:00.000Z", "utc_departure": "2023-04-22T08:05:00.000Z"}, {"id": "0a220b774c10000085c9a6d8_0", "combination_id": "0a220b774c10000085c9a6d8", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-25T14:05:00.000Z", "utc_arrival": "2023-04-25T12:05:00.000Z", "local_departure": "2023-04-25T10:55:00.000Z", "utc_departure": "2023-04-25T08:55:00.000Z"}], "booking_token": "EEHAz6ObMQ9jgX2A2EYIv62vIDbb5lfwqvicwpwKVdUS2MOQPOO79ed5IEpMwI5gzz4BiK8SZLBJAcaRlzwYpk6Mqrclbc_fTnkJnmpGbVKCMmsq0yG7hjf20XI2Ble7QhNU6FM2DeNNj1XC_KdQfqf2DvNKxYovjIqFXTb4dQ8Lo0jzCylMstSQAse2eLmwoEfVKPcanJaZv2JqXHNSaY3LkbOIDYTLsHXGJGmG8Xkl-MT7D-Jj8AOkygO1o0FBTkRsLM7HzIJO7qJH62k2MOydznWS19aUKajK4vUNcKkxt4q4Ob6sT7aKP2vsVZU6ZVXD1DkYBp3pNsb1Hrtjhd0_pEH11QpuLUoFC9q61aEZENEDe9Lx9LFxA4wfSv5SJsTEtwmbpG4aSRUZ3j-I57Pyyia3Ew6AchmePBaonArXmS_HU-QTb8bmFjdD6D4MdV8O1-ox3wOAwYrUnR__XkQMRYqhzR4qV1R_aUVVr60KHTS24349EDEeUBmUn_lyISvPtKge_Tg-XFBL325h6miK_k0bxAkEb0r6sOdH02QGzDO9XqBaxWP1Ys-MUlvDqR-NloGoBhE9IHkdw7-fIuTeKekhlMGC3wp9fUYjerL3KRYs5Om2qjGSjy-JcVzPaMyW5tv8gWgxUePeVlc8_ZoXS6hm7CGaMNFofWOrT79EyveH_Rx4YgnpUBEmQNrVDIYj6nX0vJ4S9uMPDec1J6WWWsInZ68WxcBj3DGdodBQUu6NXhBgjGAGc42_y0dRpn_NgEu-I1t5qaaXeWz_t7A==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c0d0000b8e97468_0%7C0a220b774c10000085c9a6d8_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EEHAz6ObMQ9jgX2A2EYIv62vIDbb5lfwqvicwpwKVdUS2MOQPOO79ed5IEpMwI5gzz4BiK8SZLBJAcaRlzwYpk6Mqrclbc_fTnkJnmpGbVKCMmsq0yG7hjf20XI2Ble7QhNU6FM2DeNNj1XC_KdQfqf2DvNKxYovjIqFXTb4dQ8Lo0jzCylMstSQAse2eLmwoEfVKPcanJaZv2JqXHNSaY3LkbOIDYTLsHXGJGmG8Xkl-MT7D-Jj8AOkygO1o0FBTkRsLM7HzIJO7qJH62k2MOydznWS19aUKajK4vUNcKkxt4q4Ob6sT7aKP2vsVZU6ZVXD1DkYBp3pNsb1Hrtjhd0_pEH11QpuLUoFC9q61aEZENEDe9Lx9LFxA4wfSv5SJsTEtwmbpG4aSRUZ3j-I57Pyyia3Ew6AchmePBaonArXmS_HU-QTb8bmFjdD6D4MdV8O1-ox3wOAwYrUnR__XkQMRYqhzR4qV1R_aUVVr60KHTS24349EDEeUBmUn_lyISvPtKge_Tg-XFBL325h6miK_k0bxAkEb0r6sOdH02QGzDO9XqBaxWP1Ys-MUlvDqR-NloGoBhE9IHkdw7-fIuTeKekhlMGC3wp9fUYjerL3KRYs5Om2qjGSjy-JcVzPaMyW5tv8gWgxUePeVlc8_ZoXS6hm7CGaMNFofWOrT79EyveH_Rx4YgnpUBEmQNrVDIYj6nX0vJ4S9uMPDec1J6WWWsInZ68WxcBj3DGdodBQUu6NXhBgjGAGc42_y0dRpn_NgEu-I1t5qaaXeWz_t7A==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-04-22T13:25:00.000Z", "utc_arrival": "2023-04-22T11:25:00.000Z", "local_departure": "2023-04-22T10:05:00.000Z", "utc_departure": "2023-04-22T08:05:00.000Z"}, {"id": "0b770a224c1a0000fc0feb0f_0|0a220b774c1e00004eb45e85_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 715.759277, "distance": 1975.87, "duration": {"departure": 12600, "return": 11400, "total": 24000}, "price": 214341.1826, "conversion": {"EUR": 561.092997, "HUF": 214341.1826}, "fare": {"adults": 107170.59, "children": 107170.59, "infants": 107170.59}, "bags_price": {"1": 89.208, "2": 178.416}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 6}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224c1a0000fc0feb0f_0", "combination_id": "0b770a224c1a0000fc0feb0f", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "JREG", "fare_category": "M", "fare_classes": "J", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-05T19:45:00.000Z", "utc_arrival": "2023-05-05T17:45:00.000Z", "local_departure": "2023-05-05T16:15:00.000Z", "utc_departure": "2023-05-05T14:15:00.000Z"}, {"id": "0a220b774c1e00004eb45e85_0", "combination_id": "0a220b774c1e00004eb45e85", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-09T14:05:00.000Z", "utc_arrival": "2023-05-09T12:05:00.000Z", "local_departure": "2023-05-09T10:55:00.000Z", "utc_departure": "2023-05-09T08:55:00.000Z"}], "booking_token": "EqXMJWY_ObJEuNXlpm1_gy9J4uhfuhFwklFk9vVkwz-A68x12AovFkLmSSwW6tWM6JBXE_5tea7SEa_rfZATLugtSL2ioXXgTBi1otmwchkRECacHJDs4rFeyRy2-_gTgv2qS4FgGZyGx57Bw5_ZDLCFOnqPSs1_F5L1GKlGUwaJAra2djwbUE6STowFcmMGDPlnazOkp9W4fDSvZsbd_GOtrCrc7pXnH7tt1DdvzdCamDfd9zPD3ikTJPn4qXE1lqOj6qzbqrbqRHQIBeGb79aDlgpjduvGPeohAJTrrORknbsGEr3wCOhX4xjb7teXGzZgQbZOyg2Ou8Y79I1aKTODWQsrcB6-OfLSkXaWFyvBzNHcITmvmX2cdfhzoMSP8VqGfj4-1yPNG5xkTsdubdLUhKyQ5Z78_22mGfnVV_g1Vyzexbuqzn4yJpbjoJ2Xp-Cd0joY7xzDAn1GScOClJpTrzF7jBuOVVWyFBB1d4jFlab0Ld1sJX7Io7p-RQNIS2I3J7wwIseJ_S1nIHmfkUiiNKocEV0W1ioYYVSW2XXRCtNBndaAOOnQCa49ipIJfvb6WDglr3lIb_uxHqnzCqe6T2rRwma9DdtIa7zyi3L6KlhEhcoCxIKvaY6qucaUUZAbQznTzc6P2WGVGhLykWh7h2wgyLQU9ZyUXLhtnulemXWXuWZtiBaBUXw3PurBFmONQcnaXUYlaxmO_vZvDR1jtkJdezHaVgylxb44uTyQWfP0gdFEcA5UNnsvCkEozmZacf8BsbPBB1GgARPqTNg==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c1a0000fc0feb0f_0%7C0a220b774c1e00004eb45e85_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EqXMJWY_ObJEuNXlpm1_gy9J4uhfuhFwklFk9vVkwz-A68x12AovFkLmSSwW6tWM6JBXE_5tea7SEa_rfZATLugtSL2ioXXgTBi1otmwchkRECacHJDs4rFeyRy2-_gTgv2qS4FgGZyGx57Bw5_ZDLCFOnqPSs1_F5L1GKlGUwaJAra2djwbUE6STowFcmMGDPlnazOkp9W4fDSvZsbd_GOtrCrc7pXnH7tt1DdvzdCamDfd9zPD3ikTJPn4qXE1lqOj6qzbqrbqRHQIBeGb79aDlgpjduvGPeohAJTrrORknbsGEr3wCOhX4xjb7teXGzZgQbZOyg2Ou8Y79I1aKTODWQsrcB6-OfLSkXaWFyvBzNHcITmvmX2cdfhzoMSP8VqGfj4-1yPNG5xkTsdubdLUhKyQ5Z78_22mGfnVV_g1Vyzexbuqzn4yJpbjoJ2Xp-Cd0joY7xzDAn1GScOClJpTrzF7jBuOVVWyFBB1d4jFlab0Ld1sJX7Io7p-RQNIS2I3J7wwIseJ_S1nIHmfkUiiNKocEV0W1ioYYVSW2XXRCtNBndaAOOnQCa49ipIJfvb6WDglr3lIb_uxHqnzCqe6T2rRwma9DdtIa7zyi3L6KlhEhcoCxIKvaY6qucaUUZAbQznTzc6P2WGVGhLykWh7h2wgyLQU9ZyUXLhtnulemXWXuWZtiBaBUXw3PurBFmONQcnaXUYlaxmO_vZvDR1jtkJdezHaVgylxb44uTyQWfP0gdFEcA5UNnsvCkEozmZacf8BsbPBB1GgARPqTNg==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-05T19:45:00.000Z", "utc_arrival": "2023-05-05T17:45:00.000Z", "local_departure": "2023-05-05T16:15:00.000Z", "utc_departure": "2023-05-05T14:15:00.000Z"}, {"id": "0b770a224c4100007151a3a5_0|0a220b774c440000824e9c86_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 715.837278, "distance": 1975.87, "duration": {"departure": 12000, "return": 11700, "total": 23700}, "price": 214880.3203, "conversion": {"EUR": 562.504328, "HUF": 214880.3203}, "fare": {"adults": 107440.16, "children": 110754.58, "infants": 110754.58}, "bags_price": {"1": 93.114, "2": 186.046}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 6}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224c4100007151a3a5_0", "combination_id": "0b770a224c4100007151a3a5", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-13T10:15:00.000Z", "utc_arrival": "2023-06-13T08:15:00.000Z", "local_departure": "2023-06-13T06:55:00.000Z", "utc_departure": "2023-06-13T04:55:00.000Z"}, {"id": "0a220b774c440000824e9c86_0", "combination_id": "0a220b774c440000824e9c86", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "HIREG", "fare_category": "M", "fare_classes": "H", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-16T23:45:00.000Z", "utc_arrival": "2023-06-16T21:45:00.000Z", "local_departure": "2023-06-16T20:30:00.000Z", "utc_departure": "2023-06-16T18:30:00.000Z"}], "booking_token": "EuprOl8uzplz18s7BstYCJbbywiSrye5CxNN0HOBktRHn7yJ4P-Fz-MB93Gb3QNIViyOwC2qZwLchtA4ldRkcy7_rrGWYetnyhxu7D5QnytVB5qoCnn_J65YryinpohgtE10uDPQF2MwDnM5PYca3_lcnx63JBGpdRfymeU_v1y-8yFwf_7AxAhgD2RtPSDpm735qvP9fC5Qoig1LTSGrjSPEXcDtZbHYG3Zvo9i6nea6RPZ2Zjv_FJHAEdOaMqlRmIEEFsdMQugfZ2Dg8hL5V9HVOI9m4MEkUddd2lmqgzzn9a_C0m_Clc4AzbXga9XLq6glQtu-fmWGRdsDeDHQaHuk3ZBdRgvUkXcLkGyhvgAyKK1Bq9hcG6bbnuBLeVlcR8qmyUWp0Q4d5v_EHwE1sjAz1N59qy1a_OTGHR6HbDC5PZRL30CxkjhO4cOBRex5fGQRmGNIxyIiRTH-TC3AdFJ2rWRNjmkpPZUBo9AKJqgwIKKOAq2bprzN0_bb43VahZaZ9eDGl-O7eda_2fDjHkNif4oSLg6WPbcfkhSltaJ5WhbjDUGXOdaPaAH-E0VM90Y-u149ci31a1rN1dxDiECnunlmlvSxvuwxHinu_vCl61FQv0ixjNr-qR5U7eP8qOSmUuIJWw6gUvpRgjo0WA5SMKwJFquGaUqtb3OGk6GsMWELMiTesfJu0E5zdOVqSa8G_IHw5_7Z2xBR984zg9e5lofJmBYOj4v_C137IBfG9m--xEI2vWDC1tpNthlHhfXDod8iCp-DGbwU7d44xA==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c4100007151a3a5_0%7C0a220b774c440000824e9c86_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EuprOl8uzplz18s7BstYCJbbywiSrye5CxNN0HOBktRHn7yJ4P-Fz-MB93Gb3QNIViyOwC2qZwLchtA4ldRkcy7_rrGWYetnyhxu7D5QnytVB5qoCnn_J65YryinpohgtE10uDPQF2MwDnM5PYca3_lcnx63JBGpdRfymeU_v1y-8yFwf_7AxAhgD2RtPSDpm735qvP9fC5Qoig1LTSGrjSPEXcDtZbHYG3Zvo9i6nea6RPZ2Zjv_FJHAEdOaMqlRmIEEFsdMQugfZ2Dg8hL5V9HVOI9m4MEkUddd2lmqgzzn9a_C0m_Clc4AzbXga9XLq6glQtu-fmWGRdsDeDHQaHuk3ZBdRgvUkXcLkGyhvgAyKK1Bq9hcG6bbnuBLeVlcR8qmyUWp0Q4d5v_EHwE1sjAz1N59qy1a_OTGHR6HbDC5PZRL30CxkjhO4cOBRex5fGQRmGNIxyIiRTH-TC3AdFJ2rWRNjmkpPZUBo9AKJqgwIKKOAq2bprzN0_bb43VahZaZ9eDGl-O7eda_2fDjHkNif4oSLg6WPbcfkhSltaJ5WhbjDUGXOdaPaAH-E0VM90Y-u149ci31a1rN1dxDiECnunlmlvSxvuwxHinu_vCl61FQv0ixjNr-qR5U7eP8qOSmUuIJWw6gUvpRgjo0WA5SMKwJFquGaUqtb3OGk6GsMWELMiTesfJu0E5zdOVqSa8G_IHw5_7Z2xBR984zg9e5lofJmBYOj4v_C137IBfG9m--xEI2vWDC1tpNthlHhfXDod8iCp-DGbwU7d44xA==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-13T10:15:00.000Z", "utc_arrival": "2023-06-13T08:15:00.000Z", "local_departure": "2023-06-13T06:55:00.000Z", "utc_departure": "2023-06-13T04:55:00.000Z"}, {"id": "0b770a224c2e0000339b474d_0|0a220b774c310000cf80ab4c_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 721.004276, "distance": 1975.87, "duration": {"departure": 12600, "return": 11700, "total": 24300}, "price": 215835.4657, "conversion": {"EUR": 565.004666, "HUF": 215835.4657}, "fare": {"adults": 107917.73, "children": 111120.91, "infants": 111120.91}, "bags_price": {"1": 73.64, "2": 147.266}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 439, "hold_height": 149, "hold_length": 171, "hold_weight": 20, "hold_width": 119, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 4}, "airlines": ["W6"], "route": [{"id": "0b770a224c2e0000339b474d_0", "combination_id": "0b770a224c2e0000339b474d", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "HREG", "fare_category": "M", "fare_classes": "H", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-25T21:15:00.000Z", "utc_arrival": "2023-05-25T19:15:00.000Z", "local_departure": "2023-05-25T17:45:00.000Z", "utc_departure": "2023-05-25T15:45:00.000Z"}, {"id": "0a220b774c310000cf80ab4c_0", "combination_id": "0a220b774c310000cf80ab4c", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "JKREG", "fare_category": "M", "fare_classes": "J", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-28T21:05:00.000Z", "utc_arrival": "2023-05-28T19:05:00.000Z", "local_departure": "2023-05-28T17:50:00.000Z", "utc_departure": "2023-05-28T15:50:00.000Z"}], "booking_token": "ECFMdNUELvLb0Hbvyf-H9cBoGQSFPDvi1m5JjzaY-BMvVioiB4oH75BRXTtTPhYU87lfv5arnE0Cd8RnJ7ktaasglX1AS2ysE2OejFfP_6vbrYi6U3DI9ock7x3k5c1oUol3ZDkvFp20ONW-GcnQGWYdw_Mh8qE906ZZgbLMLvaHK7yhi3A4xUhixsvsd7Xmn8yc1p3tjTPtWyphpl-f2Jyebsvz1hk1uBuO62nTZROTC_QIdIifotiV6csSFHmWO4a_oMAhactwPBToIhPW9x-Ogxn8ReT6DkWTlovcMxmehWI2nxJsu-bO49euWOfnloGc-31kUsmpFv_Wt8TP9cDPE0uIGz8jvfIIlxVzFqym0E9oShZo4Q5Ik4kcH6gHgAllMh87U2k1DsZ0C19dOnMzxS3Z0N-VyHk2eLgGmS7N5k3i1MKoGeKzlBOR_VxWECv1dz2bDa7ONChdZp0IQcErPZFZ7dhgh9E5N5_H6fik1mw_ENiraq68404YQRuMaeailxe9r7O_Z52xIJrwmhsYcWH9z5CSYnUZgv1mhkwhMdRFfHnzyPWZCclIHOHIwtmfqDZpDQRf8Yu6y2Ki3NRh1GJdQYgxFg_-c7t_-kCxZt1rIwTbCAqP_k3pTTN0wQ3R3OzXXxhNDLfkq4cC4cAexZGhDKCgn51RRiTD2v37zO0SiM8W4fsZhdPoxfq08JPLJJgxgQxy99Bo5C7XZoJI_NXtdfsyD10xrbN6hnNrPmN_PUVENkIkfANwZyls9_5s9uRY1LzSEdKlVmzKFVlfyIwnQZOSlgTlTvMUSNuA=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c2e0000339b474d_0%7C0a220b774c310000cf80ab4c_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=ECFMdNUELvLb0Hbvyf-H9cBoGQSFPDvi1m5JjzaY-BMvVioiB4oH75BRXTtTPhYU87lfv5arnE0Cd8RnJ7ktaasglX1AS2ysE2OejFfP_6vbrYi6U3DI9ock7x3k5c1oUol3ZDkvFp20ONW-GcnQGWYdw_Mh8qE906ZZgbLMLvaHK7yhi3A4xUhixsvsd7Xmn8yc1p3tjTPtWyphpl-f2Jyebsvz1hk1uBuO62nTZROTC_QIdIifotiV6csSFHmWO4a_oMAhactwPBToIhPW9x-Ogxn8ReT6DkWTlovcMxmehWI2nxJsu-bO49euWOfnloGc-31kUsmpFv_Wt8TP9cDPE0uIGz8jvfIIlxVzFqym0E9oShZo4Q5Ik4kcH6gHgAllMh87U2k1DsZ0C19dOnMzxS3Z0N-VyHk2eLgGmS7N5k3i1MKoGeKzlBOR_VxWECv1dz2bDa7ONChdZp0IQcErPZFZ7dhgh9E5N5_H6fik1mw_ENiraq68404YQRuMaeailxe9r7O_Z52xIJrwmhsYcWH9z5CSYnUZgv1mhkwhMdRFfHnzyPWZCclIHOHIwtmfqDZpDQRf8Yu6y2Ki3NRh1GJdQYgxFg_-c7t_-kCxZt1rIwTbCAqP_k3pTTN0wQ3R3OzXXxhNDLfkq4cC4cAexZGhDKCgn51RRiTD2v37zO0SiM8W4fsZhdPoxfq08JPLJJgxgQxy99Bo5C7XZoJI_NXtdfsyD10xrbN6hnNrPmN_PUVENkIkfANwZyls9_5s9uRY1LzSEdKlVmzKFVlfyIwnQZOSlgTlTvMUSNuA=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-25T21:15:00.000Z", "utc_arrival": "2023-05-25T19:15:00.000Z", "local_departure": "2023-05-25T17:45:00.000Z", "utc_departure": "2023-05-25T15:45:00.000Z"}, {"id": "0b770a224c4a00006b86e63f_0|0a220b774c4e000024b82646_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 720.05039, "distance": 1975.87, "duration": {"departure": 12600, "return": 11400, "total": 24000}, "price": 215980.4158, "conversion": {"EUR": 565.38411, "HUF": 215980.4158}, "fare": {"adults": 107990.21, "children": 111181.64, "infants": 111181.64}, "bags_price": {"1": 103.11, "2": 206.206}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 3}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224c4a00006b86e63f_0", "combination_id": "0b770a224c4a00006b86e63f", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "HREG", "fare_category": "M", "fare_classes": "H", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-22T21:15:00.000Z", "utc_arrival": "2023-06-22T19:15:00.000Z", "local_departure": "2023-06-22T17:45:00.000Z", "utc_departure": "2023-06-22T15:45:00.000Z"}, {"id": "0a220b774c4e000024b82646_0", "combination_id": "0a220b774c4e000024b82646", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-26T10:15:00.000Z", "utc_arrival": "2023-06-26T08:15:00.000Z", "local_departure": "2023-06-26T07:05:00.000Z", "utc_departure": "2023-06-26T05:05:00.000Z"}], "booking_token": "Eggoy68bcb9aes99yqzTHAcoD4X1Cj1ufSw-sRVKiJ8y--yqGMNVWRJ-zW0hE-N50EI2y9uMyYk2Mx-yVVdnS0cB8OLmPOb1ka0GFAmq5NxCvI3ZQdAy1GPlqJj9Lk1hWBDsGZqEjw9WBIMZKMrCi4sBjczlMiB_myBp50XODan0M1x3w5Yr3aR-qMqBu84xkrWY4npjr3IUra_qajOcVvVMpktzNWDS5Slelxu2reApTIAw9Oye_B84gKiHuiVbxGMUVAcXb6Zd84FAoA3T-sXiU_SlIdc8Ju8eRI6Cup-YqTPfWX1sSAb_9c13fXQPvLV_UgWbDc98PkyfRIcQOBl6JANLdSElelqwCyQ4jzezNaqzTOzukOvPs21ppABxEZ8WPWk8SfSfebs9OEyA2n8pjAMIIxvDTZYJ_blMK8fBgipIAxUktjneZU06AB7UEG7cWc1roGlZJTI1Owocf2LDCYZmZ9nQTNyzaI3to9YDUtlylXWus_yWU1fMkxEIv1_8P8HJ97lc27yJuCsn4wq4ouR3O6J_-Hdzel_jUyjDEqfGspK7cOOjxLLRJZ-FNpWEj6R_CX34KPjPVjlqN3oFN48e3qDXFDkBAXxkE6L_pTTPvoqtIpBEr7roW6l-3IhXXJnwKMkMou_PFkqGCQ5gNnJtRCebE0caT0qzatenoqKIbk7QVzCetpzGuiqA0F7x9Rck5FiB6-T2gVG50gYMJl29T0gpkdrAaBHv46GJlDFub727WD9cpTKiE3FqxdoNB_rQuQadrzpX3WQ-0llhEmOLb2K3soDzd-XqGdao=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c4a00006b86e63f_0%7C0a220b774c4e000024b82646_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=Eggoy68bcb9aes99yqzTHAcoD4X1Cj1ufSw-sRVKiJ8y--yqGMNVWRJ-zW0hE-N50EI2y9uMyYk2Mx-yVVdnS0cB8OLmPOb1ka0GFAmq5NxCvI3ZQdAy1GPlqJj9Lk1hWBDsGZqEjw9WBIMZKMrCi4sBjczlMiB_myBp50XODan0M1x3w5Yr3aR-qMqBu84xkrWY4npjr3IUra_qajOcVvVMpktzNWDS5Slelxu2reApTIAw9Oye_B84gKiHuiVbxGMUVAcXb6Zd84FAoA3T-sXiU_SlIdc8Ju8eRI6Cup-YqTPfWX1sSAb_9c13fXQPvLV_UgWbDc98PkyfRIcQOBl6JANLdSElelqwCyQ4jzezNaqzTOzukOvPs21ppABxEZ8WPWk8SfSfebs9OEyA2n8pjAMIIxvDTZYJ_blMK8fBgipIAxUktjneZU06AB7UEG7cWc1roGlZJTI1Owocf2LDCYZmZ9nQTNyzaI3to9YDUtlylXWus_yWU1fMkxEIv1_8P8HJ97lc27yJuCsn4wq4ouR3O6J_-Hdzel_jUyjDEqfGspK7cOOjxLLRJZ-FNpWEj6R_CX34KPjPVjlqN3oFN48e3qDXFDkBAXxkE6L_pTTPvoqtIpBEr7roW6l-3IhXXJnwKMkMou_PFkqGCQ5gNnJtRCebE0caT0qzatenoqKIbk7QVzCetpzGuiqA0F7x9Rck5FiB6-T2gVG50gYMJl29T0gpkdrAaBHv46GJlDFub727WD9cpTKiE3FqxdoNB_rQuQadrzpX3WQ-0llhEmOLb2K3soDzd-XqGdao=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-22T21:15:00.000Z", "utc_arrival": "2023-06-22T19:15:00.000Z", "local_departure": "2023-06-22T17:45:00.000Z", "utc_departure": "2023-06-22T15:45:00.000Z"}, {"id": "0b770a224c1900003bb4006b_0|0a220b774c1d00006b072ab9_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 720.096829, "distance": 1975.87, "duration": {"departure": 12600, "return": 11400, "total": 24000}, "price": 215998.1558, "conversion": {"EUR": 565.430549, "HUF": 215998.1558}, "fare": {"adults": 107999.08, "children": 113395.02, "infants": 113395.02}, "bags_price": {"1": 97.3, "2": 194.614}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 3}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224c1900003bb4006b_0", "combination_id": "0b770a224c1900003bb4006b", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "KLREG", "fare_category": "M", "fare_classes": "K", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-04T21:15:00.000Z", "utc_arrival": "2023-05-04T19:15:00.000Z", "local_departure": "2023-05-04T17:45:00.000Z", "utc_departure": "2023-05-04T15:45:00.000Z"}, {"id": "0a220b774c1d00006b072ab9_0", "combination_id": "0a220b774c1d00006b072ab9", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-08T10:15:00.000Z", "utc_arrival": "2023-05-08T08:15:00.000Z", "local_departure": "2023-05-08T07:05:00.000Z", "utc_departure": "2023-05-08T05:05:00.000Z"}], "booking_token": "E4eVYuaKHHkVdllqb7avVSHXHztbaJ2FARTYzmABQY2l0cNvMVPuobiXnN_ibfdMhJbHnI1rBHjJ00eAvm3R0dTf8HG32EMzDlmC6LVkBZmc4tmNshJu_avHC54J-eS1qoJljVAzSDEnu1_A0236VqO8yh1qLPGIb9Id86qpKA_mtcWt9nlmxQnjMwlorTk0PsX__QPpA4gDeWVoKLMAGfUW0I7rMhOtamsztbNzXY1kTWnz65__EnUOcZH04n6Kb4WGKRmMruY8NDe2_j4wo1LLZ01mUH0qA7hyabUg6mwSzs7iu6QYFGMUD1v7ItNtnNQ2FVssfRqk4roxgj-d8Ed98lnF5CxWQ9p46RIdijRA2nFHjDekvDSbq59llakd7DOXvo0B1GbcaUfjl4VEtSuI32dvzgV4rdPX9gwhlX08P3clUs_eM3_rpQ6oIBjOxz3-zQC3ByWGhPzba_A_ZrKDwvMzQWRRAHVNB8ukGcvgwu324ag4VN8HRXqoGNM8mZXAyrhsjfxc8JnOUlagrZVLffCyeTc8igZXbVZWUWOnP9l3qZzSpWqKNfgMI1vUW4GrvK1vb7-elovLiGYQshqMa1aJchNfGwxsv3dHcJJN-S1r4ki5a0KUskFTW1koGOloJt0VI1FhD2JRHhpAdu0eT2pu9DcQpvHG00n_XYW2hEXYv3IrECfih0C3AN4cBkV3YBdBQfehIeZhdGwPkXdbNgsERVbZNmaJaY080TF9MAJuO5gKLXQOT33cmL6f5b-gImsApkAxT4tQXEVQK2EubELlfGFG0hoZBpDp_RSw=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c1900003bb4006b_0%7C0a220b774c1d00006b072ab9_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=E4eVYuaKHHkVdllqb7avVSHXHztbaJ2FARTYzmABQY2l0cNvMVPuobiXnN_ibfdMhJbHnI1rBHjJ00eAvm3R0dTf8HG32EMzDlmC6LVkBZmc4tmNshJu_avHC54J-eS1qoJljVAzSDEnu1_A0236VqO8yh1qLPGIb9Id86qpKA_mtcWt9nlmxQnjMwlorTk0PsX__QPpA4gDeWVoKLMAGfUW0I7rMhOtamsztbNzXY1kTWnz65__EnUOcZH04n6Kb4WGKRmMruY8NDe2_j4wo1LLZ01mUH0qA7hyabUg6mwSzs7iu6QYFGMUD1v7ItNtnNQ2FVssfRqk4roxgj-d8Ed98lnF5CxWQ9p46RIdijRA2nFHjDekvDSbq59llakd7DOXvo0B1GbcaUfjl4VEtSuI32dvzgV4rdPX9gwhlX08P3clUs_eM3_rpQ6oIBjOxz3-zQC3ByWGhPzba_A_ZrKDwvMzQWRRAHVNB8ukGcvgwu324ag4VN8HRXqoGNM8mZXAyrhsjfxc8JnOUlagrZVLffCyeTc8igZXbVZWUWOnP9l3qZzSpWqKNfgMI1vUW4GrvK1vb7-elovLiGYQshqMa1aJchNfGwxsv3dHcJJN-S1r4ki5a0KUskFTW1koGOloJt0VI1FhD2JRHhpAdu0eT2pu9DcQpvHG00n_XYW2hEXYv3IrECfih0C3AN4cBkV3YBdBQfehIeZhdGwPkXdbNgsERVbZNmaJaY080TF9MAJuO5gKLXQOT33cmL6f5b-gImsApkAxT4tQXEVQK2EubELlfGFG0hoZBpDp_RSw=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-04T21:15:00.000Z", "utc_arrival": "2023-05-04T19:15:00.000Z", "local_departure": "2023-05-04T17:45:00.000Z", "utc_departure": "2023-05-04T15:45:00.000Z"}, {"id": "0b770a224c430000a78af0de_0|0a220b774c46000040adc89d_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 723.411775, "distance": 1975.87, "duration": {"departure": 12600, "return": 11700, "total": 24300}, "price": 216755.146, "conversion": {"EUR": 567.412165, "HUF": 216755.146}, "fare": {"adults": 108377.57, "children": 108377.57, "infants": 108377.57}, "bags_price": {"1": 90.986, "2": 181.972}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 439, "hold_height": 149, "hold_length": 171, "hold_weight": 20, "hold_width": 119, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 2}, "airlines": ["W6"], "route": [{"id": "0b770a224c430000a78af0de_0", "combination_id": "0b770a224c430000a78af0de", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IJREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-15T21:15:00.000Z", "utc_arrival": "2023-06-15T19:15:00.000Z", "local_departure": "2023-06-15T17:45:00.000Z", "utc_departure": "2023-06-15T15:45:00.000Z"}, {"id": "0a220b774c46000040adc89d_0", "combination_id": "0a220b774c46000040adc89d", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "JREG", "fare_category": "M", "fare_classes": "J", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-18T21:05:00.000Z", "utc_arrival": "2023-06-18T19:05:00.000Z", "local_departure": "2023-06-18T17:50:00.000Z", "utc_departure": "2023-06-18T15:50:00.000Z"}], "booking_token": "ENS-oE4HfCcGtog5rYCgqWY87mj5hDd_aFmVbggw__fVrLkhlhMpWw8wb5ZpMzWNTFFFg3MIARtMG9Epwe1ZRO1eEtVtaRo_o9VNrigf_eLzhTNHGuYTHTe_sV55ZzSo5hu3uIF3Or0u6VSRvMX9J1LNRWrUBezb-Vn5NHmWLWJKFkU4mCTZBhQ2eyn_5olEk3Wj03Z9xR2Zdce64FL3-u_lSdqZsz8DOIlZ4vrK6CmtpaaOHIp7RswaTSgQ1jWz2Sx8cF-Cyr4U8doXOq8v8t6OmNpH90m6UX3rtmvf_Roga8aPUz7zbJHMPXPrDKyu9Hh8BzJobOJpPTrYQDNHefLGmElF7fBXq0_uVOx6TzRJsAxgUgHdCTPikVdNdE-tOJ-0Yzct-9UHZ5lTfjZNURTX5Wzy3ZEGBrdcw7dxGO2WeGoPMkmP4OjWX4eoyDNjoiQquoMBtMC4Q_ti82uATs7ycVhTFqcPefYAQl_gIMZEKREVRRx43Sbeuo9BayXbUeCqMJRa1Oit_ifPRKp_cn1rwsBz-avJBOuz-nQi-33T_Kuhv-XiUen9gog8f8fTq7kvOrDgwWF-R_lNb22Yg8oOm8AgGWetkromhPvVIB1t7igFVAWFfksMbF_kmdSocmu-euYkQOX8VNrQz6SkpCFlTiSxXi2SLKIhV0oo75HWrq7PdP2iZS35wTy4NynFVsQLck8iXurnf56C1hh37NYjMpmaWKTuSAXDTZktN2E3mhUXaRv_HPW83yCi3AgWW4-3rAxjVPNf_57sG0uH_3A==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c430000a78af0de_0%7C0a220b774c46000040adc89d_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=ENS-oE4HfCcGtog5rYCgqWY87mj5hDd_aFmVbggw__fVrLkhlhMpWw8wb5ZpMzWNTFFFg3MIARtMG9Epwe1ZRO1eEtVtaRo_o9VNrigf_eLzhTNHGuYTHTe_sV55ZzSo5hu3uIF3Or0u6VSRvMX9J1LNRWrUBezb-Vn5NHmWLWJKFkU4mCTZBhQ2eyn_5olEk3Wj03Z9xR2Zdce64FL3-u_lSdqZsz8DOIlZ4vrK6CmtpaaOHIp7RswaTSgQ1jWz2Sx8cF-Cyr4U8doXOq8v8t6OmNpH90m6UX3rtmvf_Roga8aPUz7zbJHMPXPrDKyu9Hh8BzJobOJpPTrYQDNHefLGmElF7fBXq0_uVOx6TzRJsAxgUgHdCTPikVdNdE-tOJ-0Yzct-9UHZ5lTfjZNURTX5Wzy3ZEGBrdcw7dxGO2WeGoPMkmP4OjWX4eoyDNjoiQquoMBtMC4Q_ti82uATs7ycVhTFqcPefYAQl_gIMZEKREVRRx43Sbeuo9BayXbUeCqMJRa1Oit_ifPRKp_cn1rwsBz-avJBOuz-nQi-33T_Kuhv-XiUen9gog8f8fTq7kvOrDgwWF-R_lNb22Yg8oOm8AgGWetkromhPvVIB1t7igFVAWFfksMbF_kmdSocmu-euYkQOX8VNrQz6SkpCFlTiSxXi2SLKIhV0oo75HWrq7PdP2iZS35wTy4NynFVsQLck8iXurnf56C1hh37NYjMpmaWKTuSAXDTZktN2E3mhUXaRv_HPW83yCi3AgWW4-3rAxjVPNf_57sG0uH_3A==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-15T21:15:00.000Z", "utc_arrival": "2023-06-15T19:15:00.000Z", "local_departure": "2023-06-15T17:45:00.000Z", "utc_departure": "2023-06-15T15:45:00.000Z"}, {"id": "0b770a224c1e00008913fc23_0|0a220b774c21000064f4da0b_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 725.609258, "distance": 1975.87, "duration": {"departure": 11700, "return": 12900, "total": 24600}, "price": 217085.2581, "conversion": {"EUR": 568.276318, "HUF": 217085.2581}, "fare": {"adults": 108542.63, "children": 108542.63, "infants": 108542.63}, "bags_price": {"1": 88.9, "2": 187.6}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 158, "hold_height": 52, "hold_length": 78, "hold_weight": 20, "hold_width": 28, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 3, "personal_item_width": 15}, "availability": {"seats": 2}, "airlines": ["W6", "IB"], "route": [{"id": "0b770a224c1e00008913fc23_0", "combination_id": "0b770a224c1e00008913fc23", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "IB", "flight_no": 3279, "operating_carrier": "IB", "operating_flight_no": "3279", "fare_basis": "NDNNAOB4", "fare_category": "M", "fare_classes": "N", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-09T18:50:00.000Z", "utc_arrival": "2023-05-09T16:50:00.000Z", "local_departure": "2023-05-09T15:35:00.000Z", "utc_departure": "2023-05-09T13:35:00.000Z"}, {"id": "0a220b774c21000064f4da0b_0", "combination_id": "0a220b774c21000064f4da0b", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "BOREG", "fare_category": "M", "fare_classes": "B", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-13T00:05:00.000Z", "utc_arrival": "2023-05-12T22:05:00.000Z", "local_departure": "2023-05-12T20:30:00.000Z", "utc_departure": "2023-05-12T18:30:00.000Z"}], "booking_token": "E_ZiEGP3AGBRLt9cjpbpzk6VgZZukxK8kv7-5ouuDZC7puffdiuJuupTMyLKDE61a-EzW3ymNiGrrolZibmP9UFLONow2t1GC4hW0tsR6KapK_5SUupldGnr9kq_z2xzH6htSkXibyyt550Ey5yaDFIWzAB7-E84wuE5WLlze4-NWnubrN6ZwVZymmigPIDgv4giuP2eDjuZqztKK7cv-VgVzqmIzrzXy2R6mBZyxjryIexNFwm1cGBw1sPX7fOP3u4PZnfP3kIn8bddN_AfEwf0l72hqC9xiipJ0xqVeONeJzhDoA2CgYxUjkSkfLDv4DRNomToVC7sBASftkSlD8Da4DnvY4e2YGBDPoYpDKuzyBiPECsuCpXXCfzuoAYRW0SmY3p-LpUhrt2HRXwHQcbfGRht6drjpaYfL742LvAa5s2Tn2PuORcHa22TDKO2YFykTsvdjOf_eChbM5WUZdvkXi92jOfV9LUn1qutQlA4h7vSqeOTW-gNn3rkdl8xkn116KODXvRs-TStFPvGZLVej2bQstL7VWvMPinoO-O9j2vjR9j7EuWx7WqJ-1N3HLwZjvE5WWSFTKVawXfU_YqbkRLwrfo-2LOrETSDgjj5cKuR5OfrCZ75VsR5QsKwbpocQwfX0WCpQ13IAoO86b_bVe8x4d4ERvJo1bnWzDSZfGzmhCoHManZCbX8SaA7ADNNMj6vt_wwEi4Z5Vs2LcDISWcXpBQC85xeltZKOIQHQmvtwu8ox2gqw5CHI_NdWstTA3IWxRE3vmYJs7pZIrBgueIV9js7VYJ5w_qlpUby-l7xezeQQPY0_aNXZ9WhygR-uE8FrkksI0tVKVYoZDw==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c1e00008913fc23_0%7C0a220b774c21000064f4da0b_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=E_ZiEGP3AGBRLt9cjpbpzk6VgZZukxK8kv7-5ouuDZC7puffdiuJuupTMyLKDE61a-EzW3ymNiGrrolZibmP9UFLONow2t1GC4hW0tsR6KapK_5SUupldGnr9kq_z2xzH6htSkXibyyt550Ey5yaDFIWzAB7-E84wuE5WLlze4-NWnubrN6ZwVZymmigPIDgv4giuP2eDjuZqztKK7cv-VgVzqmIzrzXy2R6mBZyxjryIexNFwm1cGBw1sPX7fOP3u4PZnfP3kIn8bddN_AfEwf0l72hqC9xiipJ0xqVeONeJzhDoA2CgYxUjkSkfLDv4DRNomToVC7sBASftkSlD8Da4DnvY4e2YGBDPoYpDKuzyBiPECsuCpXXCfzuoAYRW0SmY3p-LpUhrt2HRXwHQcbfGRht6drjpaYfL742LvAa5s2Tn2PuORcHa22TDKO2YFykTsvdjOf_eChbM5WUZdvkXi92jOfV9LUn1qutQlA4h7vSqeOTW-gNn3rkdl8xkn116KODXvRs-TStFPvGZLVej2bQstL7VWvMPinoO-O9j2vjR9j7EuWx7WqJ-1N3HLwZjvE5WWSFTKVawXfU_YqbkRLwrfo-2LOrETSDgjj5cKuR5OfrCZ75VsR5QsKwbpocQwfX0WCpQ13IAoO86b_bVe8x4d4ERvJo1bnWzDSZfGzmhCoHManZCbX8SaA7ADNNMj6vt_wwEi4Z5Vs2LcDISWcXpBQC85xeltZKOIQHQmvtwu8ox2gqw5CHI_NdWstTA3IWxRE3vmYJs7pZIrBgueIV9js7VYJ5w_qlpUby-l7xezeQQPY0_aNXZ9WhygR-uE8FrkksI0tVKVYoZDw==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-09T18:50:00.000Z", "utc_arrival": "2023-05-09T16:50:00.000Z", "local_departure": "2023-05-09T15:35:00.000Z", "utc_departure": "2023-05-09T13:35:00.000Z"}, {"id": "0b770a224c2b00006e021a7d_0|0a220b774c2e0000ad0adba8_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 724.297477, "distance": 1975.87, "duration": {"departure": 12600, "return": 11700, "total": 24300}, "price": 217093.4899, "conversion": {"EUR": 568.297867, "HUF": 217093.4899}, "fare": {"adults": 108546.74, "children": 115331.76, "infants": 115331.76}, "bags_price": {"1": 83.146, "2": 166.278}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 439, "hold_height": 149, "hold_length": 171, "hold_weight": 20, "hold_width": 119, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 7}, "airlines": ["W6"], "route": [{"id": "0b770a224c2b00006e021a7d_0", "combination_id": "0b770a224c2b00006e021a7d", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-22T19:45:00.000Z", "utc_arrival": "2023-05-22T17:45:00.000Z", "local_departure": "2023-05-22T16:15:00.000Z", "utc_departure": "2023-05-22T14:15:00.000Z"}, {"id": "0a220b774c2e0000ad0adba8_0", "combination_id": "0a220b774c2e0000ad0adba8", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IJREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-26T01:15:00.000Z", "utc_arrival": "2023-05-25T23:15:00.000Z", "local_departure": "2023-05-25T22:00:00.000Z", "utc_departure": "2023-05-25T20:00:00.000Z"}], "booking_token": "EHxXAdS52HzMb4CoclYb_UcJjLoQpBPA6_TGITZ7EmaYJWh1fagBQ4KVasOAFaRvSpIAhjoKKjLEgZhp2y22ZsugzSqB0fdZyhwORQ5VlKZRXQ39RLy_9QqQdBl5JLhlZKOWasXsAKytcm1hvb737CkLE1m20YCFHlTVE9DUeaxDDOj3toWt29kaUSDlzh2KcjAku657F59Eb52x6XImVsTt4ecZZGjX1StX93NJonlaQL9_0R_fxizitoWzL0xkXzxc_oNOVt68IniDQ7qt7qOn64FIqJtOYaqol8dc3Ra0GFNzVVdVVVcbmjwwCLIny5KnGm61oMtlkeVafuPi1etBy_R4PtgRjd9_uHQTZkI7t5H8X_u_k-RoIIWj6rOI2fq3EB4eBVpSM1Rf9eHiLTuXQ3tVu7enBRZBW4XnsWQQ9KCiC4f35SnMqYdwqgnWZW0x5P5vu_DwAAgh1OhPQlIzKFKAHGYlh8QggY5DSjBfbTi9g4scvM-f58wH3BZaWvT0CBX-QDeWYBqqZhk5jzZFUHw6xfcK4kMl9aW5dU6NqRie6rM1ptEmZ5ajxl3rEzncMEEJAt8c4wnQfBcpnbeIcQW8mMVKALgOhhNe_ER3iOUEDMfd3XwwRWezJWy5lPm26lr44dMIjJECTsjyc63lD7C_nyAGs1KYOFEmkFMrIpqHWdI3qhMXZtwKViWRU0czsW7QOc5PxWfA7RiSdtcuzBcb65PgtF8Z4gb8w2_1jZ2cO9K-Xa6SHXPzdtizUaayPuIJc73GwFCmOYrnZ88RnDVMTnGSZQK_Va3Aplqs=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c2b00006e021a7d_0%7C0a220b774c2e0000ad0adba8_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EHxXAdS52HzMb4CoclYb_UcJjLoQpBPA6_TGITZ7EmaYJWh1fagBQ4KVasOAFaRvSpIAhjoKKjLEgZhp2y22ZsugzSqB0fdZyhwORQ5VlKZRXQ39RLy_9QqQdBl5JLhlZKOWasXsAKytcm1hvb737CkLE1m20YCFHlTVE9DUeaxDDOj3toWt29kaUSDlzh2KcjAku657F59Eb52x6XImVsTt4ecZZGjX1StX93NJonlaQL9_0R_fxizitoWzL0xkXzxc_oNOVt68IniDQ7qt7qOn64FIqJtOYaqol8dc3Ra0GFNzVVdVVVcbmjwwCLIny5KnGm61oMtlkeVafuPi1etBy_R4PtgRjd9_uHQTZkI7t5H8X_u_k-RoIIWj6rOI2fq3EB4eBVpSM1Rf9eHiLTuXQ3tVu7enBRZBW4XnsWQQ9KCiC4f35SnMqYdwqgnWZW0x5P5vu_DwAAgh1OhPQlIzKFKAHGYlh8QggY5DSjBfbTi9g4scvM-f58wH3BZaWvT0CBX-QDeWYBqqZhk5jzZFUHw6xfcK4kMl9aW5dU6NqRie6rM1ptEmZ5ajxl3rEzncMEEJAt8c4wnQfBcpnbeIcQW8mMVKALgOhhNe_ER3iOUEDMfd3XwwRWezJWy5lPm26lr44dMIjJECTsjyc63lD7C_nyAGs1KYOFEmkFMrIpqHWdI3qhMXZtwKViWRU0czsW7QOc5PxWfA7RiSdtcuzBcb65PgtF8Z4gb8w2_1jZ2cO9K-Xa6SHXPzdtizUaayPuIJc73GwFCmOYrnZ88RnDVMTnGSZQK_Va3Aplqs=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-22T19:45:00.000Z", "utc_arrival": "2023-05-22T17:45:00.000Z", "local_departure": "2023-05-22T16:15:00.000Z", "utc_departure": "2023-05-22T14:15:00.000Z"}, {"id": "0b770a224c1a0000e8ad793c_0|0a220b774c1d00006b072ab9_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 721.747606, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 217647.4448, "conversion": {"EUR": 569.747986, "HUF": 217647.4448}, "fare": {"adults": 108823.72, "children": 113326.31, "infants": 113326.31}, "bags_price": {"1": 70.588, "2": 141.204}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 6}, "airlines": ["FR"], "route": [{"id": "0b770a224c1a0000e8ad793c_0", "combination_id": "0b770a224c1a0000e8ad793c", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-05T21:45:00.000Z", "utc_arrival": "2023-05-05T19:45:00.000Z", "local_departure": "2023-05-05T18:25:00.000Z", "utc_departure": "2023-05-05T16:25:00.000Z"}, {"id": "0a220b774c1d00006b072ab9_0", "combination_id": "0a220b774c1d00006b072ab9", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-08T10:15:00.000Z", "utc_arrival": "2023-05-08T08:15:00.000Z", "local_departure": "2023-05-08T07:05:00.000Z", "utc_departure": "2023-05-08T05:05:00.000Z"}], "booking_token": "EnDzp_AkoAu_SMh0EnLhvsKQ3o6v9RFocRgRxIsDoeX4yZU4k8e_3wWNYBBmENacmWGvxpIWEigoi9e8oGifirU80KnY99URyjHSeehs767LBf5gE9bs7W8lC7fxEpVsH5krAAS4UrdROcQ1l6gBCYHe71bqQxYy0vemgSy19uQ56tFDxRMzQ7kanJnR2TkewATQzwt9yTCki7bhK3WQMQnqd9v5ELY1Px5UYIjT85t5PzO7yMyEPxPHQc7F-TpxnyMlmpjaho77IMa__b28fW-Feo4zBFS_fxpFkCkuSyVSEM_dBgff2oXXunUEmCTL-51ESOSDRIg8w9IBDQaKUQMFQ_TLW4_srB1PwSXQ2XC-0-rHTfaKw4998p3gyuZewJpcTxv99nq7N5Ah3pwruIWDFbGLOSItQDPU4-Fgof0-CARa0m56Yd-KqibKHYzODhUq__TEFuIjR3KnpxG0J6mLRPOs7XQhEXNxZfEEfW7tQLDviDG4T95gDlWz0kxM720bIIQfnO6CV0IRDfUqu9-xklUpXykRC_kKbl9K6KcFoAZ5EouvyX051Pa91b4FefS7FUHj23Lj-SG6SRdsLwG_WBHmOGdDYyEYhu7EXyCL1kDm6y6Ez_Fr9Uj_nGq4RpaOlB45ApcpHXgqDkfKSt6WvWyzMwJ_AEKh07T9XDmYFOuLPz34Lnl0jvskT0E1Kvh9ugXGjiRhILECJk_2AmqyR-9qKuFP27fLjzT5pXNBSv02djaNegYvmUqz2OMWk", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c1a0000e8ad793c_0%7C0a220b774c1d00006b072ab9_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EnDzp_AkoAu_SMh0EnLhvsKQ3o6v9RFocRgRxIsDoeX4yZU4k8e_3wWNYBBmENacmWGvxpIWEigoi9e8oGifirU80KnY99URyjHSeehs767LBf5gE9bs7W8lC7fxEpVsH5krAAS4UrdROcQ1l6gBCYHe71bqQxYy0vemgSy19uQ56tFDxRMzQ7kanJnR2TkewATQzwt9yTCki7bhK3WQMQnqd9v5ELY1Px5UYIjT85t5PzO7yMyEPxPHQc7F-TpxnyMlmpjaho77IMa__b28fW-Feo4zBFS_fxpFkCkuSyVSEM_dBgff2oXXunUEmCTL-51ESOSDRIg8w9IBDQaKUQMFQ_TLW4_srB1PwSXQ2XC-0-rHTfaKw4998p3gyuZewJpcTxv99nq7N5Ah3pwruIWDFbGLOSItQDPU4-Fgof0-CARa0m56Yd-KqibKHYzODhUq__TEFuIjR3KnpxG0J6mLRPOs7XQhEXNxZfEEfW7tQLDviDG4T95gDlWz0kxM720bIIQfnO6CV0IRDfUqu9-xklUpXykRC_kKbl9K6KcFoAZ5EouvyX051Pa91b4FefS7FUHj23Lj-SG6SRdsLwG_WBHmOGdDYyEYhu7EXyCL1kDm6y6Ez_Fr9Uj_nGq4RpaOlB45ApcpHXgqDkfKSt6WvWyzMwJ_AEKh07T9XDmYFOuLPz34Lnl0jvskT0E1Kvh9ugXGjiRhILECJk_2AmqyR-9qKuFP27fLjzT5pXNBSv02djaNegYvmUqz2OMWk", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-05T21:45:00.000Z", "utc_arrival": "2023-05-05T19:45:00.000Z", "local_departure": "2023-05-05T18:25:00.000Z", "utc_departure": "2023-05-05T16:25:00.000Z"}, {"id": "0b770a224c2b00007aa0884e_0|0a220b774c2f0000a02e0875_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 722.199759, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 217820.1702, "conversion": {"EUR": 570.200139, "HUF": 217820.1702}, "fare": {"adults": 108910.09, "children": 113350.37, "infants": 113350.37}, "bags_price": {"1": 71.05, "2": 142.114}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 6}, "airlines": ["FR"], "route": [{"id": "0b770a224c2b00007aa0884e_0", "combination_id": "0b770a224c2b00007aa0884e", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-22T14:00:00.000Z", "utc_arrival": "2023-05-22T12:00:00.000Z", "local_departure": "2023-05-22T10:40:00.000Z", "utc_departure": "2023-05-22T08:40:00.000Z"}, {"id": "0a220b774c2f0000a02e0875_0", "combination_id": "0a220b774c2f0000a02e0875", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-26T18:00:00.000Z", "utc_arrival": "2023-05-26T16:00:00.000Z", "local_departure": "2023-05-26T14:50:00.000Z", "utc_departure": "2023-05-26T12:50:00.000Z"}], "booking_token": "Elw_fvbqiMF9uk1r7_BkceBFLWkIGq5SnraV533nJjNjcfPAzBUbZOza8B3wTk0eQjrnXD2vFteGqp50UnANLTa_glueVMWp3j_MrvX9vQ_XM5Wx6QjyiXhZZgzKA0fGWKtk_O_M22M3HmfeuRxUws67-WKOov0n4PeYzXAZoqDDQf9TivVUsYgzv9Y4NxCVqwBmb_G4DrdcXcQBvmOiMdpGO5CY747Gd2z6ZdrHZ26C9Un6Y0-cLnv2QYpzUwQ0Z182bYr9XKcYZQGTvXzlUACnqY4t3sDPSokVJYQglNySJ3-0s1ybYb5qk1fyXctR6h3DcTjoRViI4qI5mEfYcHp-Um_JLfJKa9usCrzCxJP8Ftp5-d40RjDfMM-JzWEYs4z3db-Ze9t2R7ZNdig56RCRHsdWHx6sv4-aN-puQpSO5fmd_Bw9mUwcRH2k4Y__9kuTZEvvB7WsvOLGJGEVmA6Ti_qmgPNSExbwBmQ2SFXNZpdE9MZObcrGd1Y53xq5FkqfPR4vKIkyR0SpCwYEm5S2HsrNZkM2AJ_9tZhNGW7U5h08HtErq2jmsC-wKB1Fygs4fQo6Ts91Dhc3QGwrbwXrCYYsb6y_FjLxLvnQLK-OQBh0pjWgzVARc7FgTLmwrVku44z7Z8bzPaabzloiN1dhVaR3qqgTBDN9kN8SG4kU91mCziu82iTzbVfoDJvIh2taWMPp6GGM7mYf5JS1CxrI63hW28lkPNFDAPit2CNc=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c2b00007aa0884e_0%7C0a220b774c2f0000a02e0875_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=Elw_fvbqiMF9uk1r7_BkceBFLWkIGq5SnraV533nJjNjcfPAzBUbZOza8B3wTk0eQjrnXD2vFteGqp50UnANLTa_glueVMWp3j_MrvX9vQ_XM5Wx6QjyiXhZZgzKA0fGWKtk_O_M22M3HmfeuRxUws67-WKOov0n4PeYzXAZoqDDQf9TivVUsYgzv9Y4NxCVqwBmb_G4DrdcXcQBvmOiMdpGO5CY747Gd2z6ZdrHZ26C9Un6Y0-cLnv2QYpzUwQ0Z182bYr9XKcYZQGTvXzlUACnqY4t3sDPSokVJYQglNySJ3-0s1ybYb5qk1fyXctR6h3DcTjoRViI4qI5mEfYcHp-Um_JLfJKa9usCrzCxJP8Ftp5-d40RjDfMM-JzWEYs4z3db-Ze9t2R7ZNdig56RCRHsdWHx6sv4-aN-puQpSO5fmd_Bw9mUwcRH2k4Y__9kuTZEvvB7WsvOLGJGEVmA6Ti_qmgPNSExbwBmQ2SFXNZpdE9MZObcrGd1Y53xq5FkqfPR4vKIkyR0SpCwYEm5S2HsrNZkM2AJ_9tZhNGW7U5h08HtErq2jmsC-wKB1Fygs4fQo6Ts91Dhc3QGwrbwXrCYYsb6y_FjLxLvnQLK-OQBh0pjWgzVARc7FgTLmwrVku44z7Z8bzPaabzloiN1dhVaR3qqgTBDN9kN8SG4kU91mCziu82iTzbVfoDJvIh2taWMPp6GGM7mYf5JS1CxrI63hW28lkPNFDAPit2CNc=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-22T14:00:00.000Z", "utc_arrival": "2023-05-22T12:00:00.000Z", "local_departure": "2023-05-22T10:40:00.000Z", "utc_departure": "2023-05-22T08:40:00.000Z"}, {"id": "0b770a224c09000063e5c3d1_0|0a220b774c0d0000c87689a1_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 722.349499, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 217877.3719, "conversion": {"EUR": 570.349879, "HUF": 217877.3719}, "fare": {"adults": 108938.69, "children": 108938.69, "infants": 108938.69}, "bags_price": {"1": 71.05, "2": 142.114}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 6}, "airlines": ["FR"], "route": [{"id": "0b770a224c09000063e5c3d1_0", "combination_id": "0b770a224c09000063e5c3d1", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-18T10:15:00.000Z", "utc_arrival": "2023-04-18T08:15:00.000Z", "local_departure": "2023-04-18T06:55:00.000Z", "utc_departure": "2023-04-18T04:55:00.000Z"}, {"id": "0a220b774c0d0000c87689a1_0", "combination_id": "0a220b774c0d0000c87689a1", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-22T09:40:00.000Z", "utc_arrival": "2023-04-22T07:40:00.000Z", "local_departure": "2023-04-22T06:30:00.000Z", "utc_departure": "2023-04-22T04:30:00.000Z"}], "booking_token": "EsC-n1aIZlvrKzoy89xW1uLnlZodHWlQgBkGSW4CAA1vM4mmszA0sYbdQwi3GOTV1qLrz6UAUKhkxoTiEPT89jkMXs8jQpivAZzt8PnQJJGltwxOGNyxpTPggeSpWhsA4o9Em-8EYzD5bmig5wacTJkWsRy8NcVEK9TnLQu0QB3984frG_ivS4Y7SZpM0R1-LRIU0jKT1zqlpGxLgE0UypUH-Acq18divfxUlAkLZDTZkn0NAOP1mGgaEK5hhdobZ3AybqHd0XhocT6lkErF2y2zgilxnDvlZVSCZH6s1bnErgq-0UVc-vZfP7dXSdO5b3pcEPApJu3fbVE3BK1tAoPtER6yoC8Aovg5SLlma7kiuG_JnAADM6pKSXJ3axRanUzJSb2OWp1sSLShE7fpxXjbvT9wCX8k_QWMjIemqTvV7Cv9FeDpPVTRzr9sYOWDiQg7sllVVfjUuOXB8scyyFeskULQT9thThZ99145vWU3vn2fWwKFAKmDcFlCnyPkpeNwzAGwA_wSt2TREiVDQMDIc-0tpL3jRRCN2jcA48U_eOZ3bTC0T8mPwa1fLdHvyvqct650iwKrE0jDOSign3HDiD759IYRNnjHbHbr6n73f2E-XQ-n2tmiDRedkcq4CnH3nrT2OE4QqUUJ8kczu6he8ydIVl0VAPuqpyw0VnNA2oPvnNIyWW7wKecCf03IE1UbW1_xKl0woa4HfdN3T7A==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c09000063e5c3d1_0%7C0a220b774c0d0000c87689a1_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EsC-n1aIZlvrKzoy89xW1uLnlZodHWlQgBkGSW4CAA1vM4mmszA0sYbdQwi3GOTV1qLrz6UAUKhkxoTiEPT89jkMXs8jQpivAZzt8PnQJJGltwxOGNyxpTPggeSpWhsA4o9Em-8EYzD5bmig5wacTJkWsRy8NcVEK9TnLQu0QB3984frG_ivS4Y7SZpM0R1-LRIU0jKT1zqlpGxLgE0UypUH-Acq18divfxUlAkLZDTZkn0NAOP1mGgaEK5hhdobZ3AybqHd0XhocT6lkErF2y2zgilxnDvlZVSCZH6s1bnErgq-0UVc-vZfP7dXSdO5b3pcEPApJu3fbVE3BK1tAoPtER6yoC8Aovg5SLlma7kiuG_JnAADM6pKSXJ3axRanUzJSb2OWp1sSLShE7fpxXjbvT9wCX8k_QWMjIemqTvV7Cv9FeDpPVTRzr9sYOWDiQg7sllVVfjUuOXB8scyyFeskULQT9thThZ99145vWU3vn2fWwKFAKmDcFlCnyPkpeNwzAGwA_wSt2TREiVDQMDIc-0tpL3jRRCN2jcA48U_eOZ3bTC0T8mPwa1fLdHvyvqct650iwKrE0jDOSign3HDiD759IYRNnjHbHbr6n73f2E-XQ-n2tmiDRedkcq4CnH3nrT2OE4QqUUJ8kczu6he8ydIVl0VAPuqpyw0VnNA2oPvnNIyWW7wKecCf03IE1UbW1_xKl0woa4HfdN3T7A==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-04-18T10:15:00.000Z", "utc_arrival": "2023-04-18T08:15:00.000Z", "local_departure": "2023-04-18T06:55:00.000Z", "utc_departure": "2023-04-18T04:55:00.000Z"}, {"id": "0b770a224c3c0000c3c77655_0|0a220b774c400000ebc98d9f_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 726.441053, "distance": 1975.87, "duration": {"departure": 12600, "return": 11700, "total": 24300}, "price": 217912.3499, "conversion": {"EUR": 570.441443, "HUF": 217912.3499}, "fare": {"adults": 108956.17, "children": 112291.1, "infants": 112291.1}, "bags_price": {"1": 105.924, "2": 211.848}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 439, "hold_height": 149, "hold_length": 171, "hold_weight": 20, "hold_width": 119, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 2}, "airlines": ["W6"], "route": [{"id": "0b770a224c3c0000c3c77655_0", "combination_id": "0b770a224c3c0000c3c77655", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "HIREG", "fare_category": "M", "fare_classes": "H", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-08T21:15:00.000Z", "utc_arrival": "2023-06-08T19:15:00.000Z", "local_departure": "2023-06-08T17:45:00.000Z", "utc_departure": "2023-06-08T15:45:00.000Z"}, {"id": "0a220b774c400000ebc98d9f_0", "combination_id": "0a220b774c400000ebc98d9f", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "JREG", "fare_category": "M", "fare_classes": "J", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-12T23:45:00.000Z", "utc_arrival": "2023-06-12T21:45:00.000Z", "local_departure": "2023-06-12T20:30:00.000Z", "utc_departure": "2023-06-12T18:30:00.000Z"}], "booking_token": "EXZF7EAwwxpmzYu7hPrSPnAwk-hLQMk-Ps2RrxjqBQo8Z9LQO-f2CcWeU7zFawnIF2qJv9JVLZL4Wrk1QKp1dtd8jugtyO3irn0amEDdd-vPvJcZriPGLsRul3Cuh2iH-7R-mJUjr_5YfWiut6D4dmo0UH9wkW_eUiawfQcMMFpzo8f-rnvbpLvNui5Tv85BhJLO1qmLyTm5pH81pc2P3y4EbWrT4TLN628-sWYOqpfmE89Lwui-ZAMw1nQ_CteJJahgwkwklLweiNdKMEqnZrS8WaHQpVYfcPkH0viku1jeDgm46sPXEPU-_v9t8EDWMpIJDQ90kZ8wlceO06sJgnqci2ZYKdtUUGyjH_GccjCZkqMwTtbzLWO3ngXm-dzy9_1hWFD6LvlB83LN2Ir93zspHso3OXE7BhfZmgzLPFU_OITclCXW45fkm9vzVofZ29bdp4xFwHhX88Y117IXUqRy38_CuWCDmEJWf5nViJxR1sMD2BCgM-d_4snnsKGJpoZnQMW5cH_pKQbDfORdJMn91X9vC2zy3Z__S_2JkPHHiH5GjtRBWTyd7_EoLlypabbBhx92RyE_h6oMley7i8tH0Q3CyfKDpEczQQUeTDLoeOdQoqLcidZmmWYxA5rCsYxacgxFqOln1TX1Vmnd9TttgUjfuk5XJoBfD4a9hBy_Cu5nJIj5RDR1Uxt2CC7JlOk5pd0PiS4QGdwKnA7UYdN2A-KhjujmmhOY6RXc6HMz0hlB8oPGr_pIGQ6DBK5tqCO5h2Aw4juv8z3DLHoNzm6YKyqnJ_kQR7hPXpMOBIBACKOaYyzwvXBZ2N7Q3G6uh", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c3c0000c3c77655_0%7C0a220b774c400000ebc98d9f_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EXZF7EAwwxpmzYu7hPrSPnAwk-hLQMk-Ps2RrxjqBQo8Z9LQO-f2CcWeU7zFawnIF2qJv9JVLZL4Wrk1QKp1dtd8jugtyO3irn0amEDdd-vPvJcZriPGLsRul3Cuh2iH-7R-mJUjr_5YfWiut6D4dmo0UH9wkW_eUiawfQcMMFpzo8f-rnvbpLvNui5Tv85BhJLO1qmLyTm5pH81pc2P3y4EbWrT4TLN628-sWYOqpfmE89Lwui-ZAMw1nQ_CteJJahgwkwklLweiNdKMEqnZrS8WaHQpVYfcPkH0viku1jeDgm46sPXEPU-_v9t8EDWMpIJDQ90kZ8wlceO06sJgnqci2ZYKdtUUGyjH_GccjCZkqMwTtbzLWO3ngXm-dzy9_1hWFD6LvlB83LN2Ir93zspHso3OXE7BhfZmgzLPFU_OITclCXW45fkm9vzVofZ29bdp4xFwHhX88Y117IXUqRy38_CuWCDmEJWf5nViJxR1sMD2BCgM-d_4snnsKGJpoZnQMW5cH_pKQbDfORdJMn91X9vC2zy3Z__S_2JkPHHiH5GjtRBWTyd7_EoLlypabbBhx92RyE_h6oMley7i8tH0Q3CyfKDpEczQQUeTDLoeOdQoqLcidZmmWYxA5rCsYxacgxFqOln1TX1Vmnd9TttgUjfuk5XJoBfD4a9hBy_Cu5nJIj5RDR1Uxt2CC7JlOk5pd0PiS4QGdwKnA7UYdN2A-KhjujmmhOY6RXc6HMz0hlB8oPGr_pIGQ6DBK5tqCO5h2Aw4juv8z3DLHoNzm6YKyqnJ_kQR7hPXpMOBIBACKOaYyzwvXBZ2N7Q3G6uh", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-08T21:15:00.000Z", "utc_arrival": "2023-06-08T19:15:00.000Z", "local_departure": "2023-06-08T17:45:00.000Z", "utc_departure": "2023-06-08T15:45:00.000Z"}, {"id": "0b770a224bf60000a70051c8_0|0a220b774bf90000509b8e91_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 727.298755, "distance": 1975.87, "duration": {"departure": 12600, "return": 11700, "total": 24300}, "price": 218239.9977, "conversion": {"EUR": 571.299145, "HUF": 218239.9977}, "fare": {"adults": 109120, "children": 109120, "infants": 109120}, "bags_price": {"1": 97.342, "2": 194.684}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 439, "hold_height": 149, "hold_length": 171, "hold_weight": 20, "hold_width": 119, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 2}, "airlines": ["W6"], "route": [{"id": "0b770a224bf60000a70051c8_0", "combination_id": "0b770a224bf60000a70051c8", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "JKREG", "fare_category": "M", "fare_classes": "J", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-03-30T21:15:00.000Z", "utc_arrival": "2023-03-30T19:15:00.000Z", "local_departure": "2023-03-30T17:45:00.000Z", "utc_departure": "2023-03-30T15:45:00.000Z"}, {"id": "0a220b774bf90000509b8e91_0", "combination_id": "0a220b774bf90000509b8e91", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "HIREG", "fare_category": "M", "fare_classes": "H", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-02T21:05:00.000Z", "utc_arrival": "2023-04-02T19:05:00.000Z", "local_departure": "2023-04-02T17:50:00.000Z", "utc_departure": "2023-04-02T15:50:00.000Z"}], "booking_token": "EY4kkSd4yb9ZWdJ-6Qi2XPa_gdMa28xFQfI1R4QUYH990HG_MUd2M9ezrCCuaIRsbco9fHz0G20egor4gOZjA9mZW8ufCtOg5f8gKk8JMMZF0X_7q6lb5CC7wiLhQ9br4OKoAeexXWyRzJXeEmbd7Rp8wbjUti69-Jk-NMKDI_ct9e5Qqh-suBAQSPE5s6yZlXGRBXvINk2t7OQ3UrEiipn5XCokFkxRY_53L-5OyCmsBWbJj-cCTFQqsAYQNYkdouwItMKeHPLTA93ymJpZTFwWDIJWsAW0mnkRl0ZBz2XVUFQ259zaSDjjY6l--7slpzN5Z-SZxGKsLC6gjyFc45dx1LV2acJgp64uUDOvraR0kUddnMmCVREuuswhTFZ2Jizl3aO_cAw9SkKphSnCxcMFYfdm7wQYxFruHfZPfNvBBFD9LFtUIM2rk9wB9RrtBn4FNm1-vMIR_JxyHqlxwZ4EHVqKl-aqSdGr4w1bVXYpEXjR_6Ow4W7tZhyFVGksjnlx9nERewHTSTV2LlaxmisaMZRLKTB7ynfr3902xpw9MTwCPte0SYl1Ufjusvt9SVRV3KCCaGNg9r61XGaq0SQSjnkPF0cpZG3HqnaqNA9ydy-_u5koShQLN6437SpyNOfLk6uz1ihm1J_oYiJ9CijrlBr9Yhf53FNwZKpOjrRHY6KBffGqXgEtv1Ss5Lqs7Rmvd6n10CSjKB0X8fspjzRazY6nrx2CripI-FK8pOdw50MNHPq7iPdaxWm3VFoUuKnSOnUVL4tPU6lDmi2nN7QXKCMCiv8i4H_R_gc0B8nw=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224bf60000a70051c8_0%7C0a220b774bf90000509b8e91_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EY4kkSd4yb9ZWdJ-6Qi2XPa_gdMa28xFQfI1R4QUYH990HG_MUd2M9ezrCCuaIRsbco9fHz0G20egor4gOZjA9mZW8ufCtOg5f8gKk8JMMZF0X_7q6lb5CC7wiLhQ9br4OKoAeexXWyRzJXeEmbd7Rp8wbjUti69-Jk-NMKDI_ct9e5Qqh-suBAQSPE5s6yZlXGRBXvINk2t7OQ3UrEiipn5XCokFkxRY_53L-5OyCmsBWbJj-cCTFQqsAYQNYkdouwItMKeHPLTA93ymJpZTFwWDIJWsAW0mnkRl0ZBz2XVUFQ259zaSDjjY6l--7slpzN5Z-SZxGKsLC6gjyFc45dx1LV2acJgp64uUDOvraR0kUddnMmCVREuuswhTFZ2Jizl3aO_cAw9SkKphSnCxcMFYfdm7wQYxFruHfZPfNvBBFD9LFtUIM2rk9wB9RrtBn4FNm1-vMIR_JxyHqlxwZ4EHVqKl-aqSdGr4w1bVXYpEXjR_6Ow4W7tZhyFVGksjnlx9nERewHTSTV2LlaxmisaMZRLKTB7ynfr3902xpw9MTwCPte0SYl1Ufjusvt9SVRV3KCCaGNg9r61XGaq0SQSjnkPF0cpZG3HqnaqNA9ydy-_u5koShQLN6437SpyNOfLk6uz1ihm1J_oYiJ9CijrlBr9Yhf53FNwZKpOjrRHY6KBffGqXgEtv1Ss5Lqs7Rmvd6n10CSjKB0X8fspjzRazY6nrx2CripI-FK8pOdw50MNHPq7iPdaxWm3VFoUuKnSOnUVL4tPU6lDmi2nN7QXKCMCiv8i4H_R_gc0B8nw=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-03-30T21:15:00.000Z", "utc_arrival": "2023-03-30T19:15:00.000Z", "local_departure": "2023-03-30T17:45:00.000Z", "utc_departure": "2023-03-30T15:45:00.000Z"}, {"id": "0b770a224c40000061fa8349_0|0a220b774c44000078e26f99_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 723.785428, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 218425.9061, "conversion": {"EUR": 571.785808, "HUF": 218425.9061}, "fare": {"adults": 109212.95, "children": 109212.95, "infants": 109212.95}, "bags_price": {"1": 77.77, "2": 155.526}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 5}, "airlines": ["FR"], "route": [{"id": "0b770a224c40000061fa8349_0", "combination_id": "0b770a224c40000061fa8349", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-12T14:00:00.000Z", "utc_arrival": "2023-06-12T12:00:00.000Z", "local_departure": "2023-06-12T10:40:00.000Z", "utc_departure": "2023-06-12T08:40:00.000Z"}, {"id": "0a220b774c44000078e26f99_0", "combination_id": "0a220b774c44000078e26f99", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-16T18:00:00.000Z", "utc_arrival": "2023-06-16T16:00:00.000Z", "local_departure": "2023-06-16T14:50:00.000Z", "utc_departure": "2023-06-16T12:50:00.000Z"}], "booking_token": "EhCe9Hig2W9Pu-KUQIHitXus8TfSxkVMy0sdbfOj6Hk122QdwhRGdIJ-usdwlFB-axRfSVJ7iyu5XxCaXoiWfueUxdCw1ux5EVRIRoDY2n9GcnlP6VxwE1qFUD4jPbVdZbQooKfHKxAz1PTrw0GUdF8uxb-pIS39wsfzpEXSj8DDNj7_Hwxvj6j15YqvPu3iggiEveVRxbx6It90gZ2jbWeQuo-H3myic_0QX05w18cPwXP9_CMg1cvuzaqCslaJniZFu13VZRsM7eDB9lYueF8UB_hVSi7IFtZY0mlQjS3noJP7nh5EF5GTXyrpa-nYBLgWTy_9sCjjMae8myxpb8i-fz2Y93vg5MYzOE-dh8cCaKyfyu1DvM4tG9vmL85Ia6oOYAWkHIZRj1j0iWgu_kQRpxFrH8BdRUut1xufgn7Sna3slFTjy1aSGXRQxUreSwJ3NavnRuwIhPJTyJQPt5Y_Q_6TrSuMB76QYPWCnPvH5c-9-3BQ1xcMCS-USTBpQDAHRpKZsBnWRj196vk3E9F7sryf8BbX-k2jxwnP3X1ga-lvKFKWLbpVOvtFG3dvyIEeKpGYpjNarSF60hoOUauD9DNMjjWQ3iA8E5J4gJ2XZPuTIIIc20mfra276WjTZPyPfBD4So8oNBVNsb1YtvEPtyyrryhDy73KuyDH6aKkJoXUxYAOjLLqGZBAEQXozxIVG_hxH3XX7XIcvioKnklNBaqs46X1XKKtKsP4Ts1aIwp2ws5x6PZgbwOZU_2mX3nLDE37K15E4Wzsb71TyTQ==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c40000061fa8349_0%7C0a220b774c44000078e26f99_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EhCe9Hig2W9Pu-KUQIHitXus8TfSxkVMy0sdbfOj6Hk122QdwhRGdIJ-usdwlFB-axRfSVJ7iyu5XxCaXoiWfueUxdCw1ux5EVRIRoDY2n9GcnlP6VxwE1qFUD4jPbVdZbQooKfHKxAz1PTrw0GUdF8uxb-pIS39wsfzpEXSj8DDNj7_Hwxvj6j15YqvPu3iggiEveVRxbx6It90gZ2jbWeQuo-H3myic_0QX05w18cPwXP9_CMg1cvuzaqCslaJniZFu13VZRsM7eDB9lYueF8UB_hVSi7IFtZY0mlQjS3noJP7nh5EF5GTXyrpa-nYBLgWTy_9sCjjMae8myxpb8i-fz2Y93vg5MYzOE-dh8cCaKyfyu1DvM4tG9vmL85Ia6oOYAWkHIZRj1j0iWgu_kQRpxFrH8BdRUut1xufgn7Sna3slFTjy1aSGXRQxUreSwJ3NavnRuwIhPJTyJQPt5Y_Q_6TrSuMB76QYPWCnPvH5c-9-3BQ1xcMCS-USTBpQDAHRpKZsBnWRj196vk3E9F7sryf8BbX-k2jxwnP3X1ga-lvKFKWLbpVOvtFG3dvyIEeKpGYpjNarSF60hoOUauD9DNMjjWQ3iA8E5J4gJ2XZPuTIIIc20mfra276WjTZPyPfBD4So8oNBVNsb1YtvEPtyyrryhDy73KuyDH6aKkJoXUxYAOjLLqGZBAEQXozxIVG_hxH3XX7XIcvioKnklNBaqs46X1XKKtKsP4Ts1aIwp2ws5x6PZgbwOZU_2mX3nLDE37K15E4Wzsb71TyTQ==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-12T14:00:00.000Z", "utc_arrival": "2023-06-12T12:00:00.000Z", "local_departure": "2023-06-12T10:40:00.000Z", "utc_departure": "2023-06-12T08:40:00.000Z"}, {"id": "0b770a224c390000c8acc8ed_0|0a220b774c3d000018fc23d3_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 733.403515, "distance": 1975.87, "duration": {"departure": 12600, "return": 12900, "total": 25500}, "price": 218534.6928, "conversion": {"EUR": 572.070585, "HUF": 218534.6928}, "fare": {"adults": 109267.35, "children": 112510.59, "infants": 112510.59}, "bags_price": {"1": 110.124, "2": 220.248}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 439, "hold_height": 149, "hold_length": 171, "hold_weight": 20, "hold_width": 119, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 2}, "airlines": ["W6"], "route": [{"id": "0b770a224c390000c8acc8ed_0", "combination_id": "0b770a224c390000c8acc8ed", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "HREG", "fare_category": "M", "fare_classes": "H", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-05T19:45:00.000Z", "utc_arrival": "2023-06-05T17:45:00.000Z", "local_departure": "2023-06-05T16:15:00.000Z", "utc_departure": "2023-06-05T14:15:00.000Z"}, {"id": "0a220b774c3d000018fc23d3_0", "combination_id": "0a220b774c3d000018fc23d3", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "JKREG", "fare_category": "M", "fare_classes": "J", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-10T01:05:00.000Z", "utc_arrival": "2023-06-09T23:05:00.000Z", "local_departure": "2023-06-09T21:30:00.000Z", "utc_departure": "2023-06-09T19:30:00.000Z"}], "booking_token": "Ewekc3bxz4P4NsmWKDtUlfiDGZsl2jxzdV37CwSOrVIWocntbQX-cPXKTKaPRJ5KR-3Cw_Mp14IQ15Io3Fz-IlAq1TOCQB-lNq_JglFbD5x71sa76RI4RkZTpUmNH2zqyASim_1ncxKoE4KRdDBr-AHewolvwJfXLacTmqTOlFtREeB-n2-7A5VgUc1GH4I1SH0n3Wm_c1cpPVIxJnek9uuxqM2FKYe_Sx7MroD5uAaHV_6EZlpRR64fvt2fSgZ8AkwiI5ZEzIWqythJQwd-CLXtk0Gqt1GO3jgl38pY4kTTMeoChGy0vqRxuFaZVxpoZz_Suf0HDBrmNOprT0XBtgZyCCKgLjzwWqUBY6P33l64jSfKY-arTJcQVx0EGoJUVjdfto1H3o4ONwZbC4JeCIHnBfryzWtmLY01zlQN2JVa9iddaOyFx4koF6O-vx406fX3FQFmN1iHSJHVNPvB0mzVbnpp09yLDcvO97-fDlNCjn1mwWmIE13ojdV8dIQJ1KtiEo_glO8ameWPHr8Ra_MIhPgEbMb8CyifgpHo_Qy9jhYH5pXLy2kl6aQnUy_z_g4-StMGGsR0XDkRD2-PjFeRnlGAoCSUQeCACbPZxChnjpeglCHu23CeFmzE4kd0j1XamFM0YLlkaOSIzfwh9xgi8bJK8c8dnxMel9NNukOWHzUsxkMbpuGGKxV1mobRXiQXJVF42Ob6BS8UDpO2BbmanGN4rG4_7Pv0VVBmJs5a3tYKQGOtkKgmiSQiAEovh1HiE_pvN0pCSSzCunU-GNBaPV3kS_3XjImwfpIwbjUA=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c390000c8acc8ed_0%7C0a220b774c3d000018fc23d3_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=Ewekc3bxz4P4NsmWKDtUlfiDGZsl2jxzdV37CwSOrVIWocntbQX-cPXKTKaPRJ5KR-3Cw_Mp14IQ15Io3Fz-IlAq1TOCQB-lNq_JglFbD5x71sa76RI4RkZTpUmNH2zqyASim_1ncxKoE4KRdDBr-AHewolvwJfXLacTmqTOlFtREeB-n2-7A5VgUc1GH4I1SH0n3Wm_c1cpPVIxJnek9uuxqM2FKYe_Sx7MroD5uAaHV_6EZlpRR64fvt2fSgZ8AkwiI5ZEzIWqythJQwd-CLXtk0Gqt1GO3jgl38pY4kTTMeoChGy0vqRxuFaZVxpoZz_Suf0HDBrmNOprT0XBtgZyCCKgLjzwWqUBY6P33l64jSfKY-arTJcQVx0EGoJUVjdfto1H3o4ONwZbC4JeCIHnBfryzWtmLY01zlQN2JVa9iddaOyFx4koF6O-vx406fX3FQFmN1iHSJHVNPvB0mzVbnpp09yLDcvO97-fDlNCjn1mwWmIE13ojdV8dIQJ1KtiEo_glO8ameWPHr8Ra_MIhPgEbMb8CyifgpHo_Qy9jhYH5pXLy2kl6aQnUy_z_g4-StMGGsR0XDkRD2-PjFeRnlGAoCSUQeCACbPZxChnjpeglCHu23CeFmzE4kd0j1XamFM0YLlkaOSIzfwh9xgi8bJK8c8dnxMel9NNukOWHzUsxkMbpuGGKxV1mobRXiQXJVF42Ob6BS8UDpO2BbmanGN4rG4_7Pv0VVBmJs5a3tYKQGOtkKgmiSQiAEovh1HiE_pvN0pCSSzCunU-GNBaPV3kS_3XjImwfpIwbjUA=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-05T19:45:00.000Z", "utc_arrival": "2023-06-05T17:45:00.000Z", "local_departure": "2023-06-05T16:15:00.000Z", "utc_departure": "2023-06-05T14:15:00.000Z"}, {"id": "0b770a224c05000004bc72da_0|0a220b774c080000c0858f1c_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 725.409151, "distance": 1975.87, "duration": {"departure": 12000, "return": 11700, "total": 23700}, "price": 218536.8381, "conversion": {"EUR": 572.076201, "HUF": 218536.8381}, "fare": {"adults": 109268.42, "children": 109268.42, "infants": 109268.42}, "bags_price": {"1": 116.844, "2": 233.674}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 2}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224c05000004bc72da_0", "combination_id": "0b770a224c05000004bc72da", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-14T21:45:00.000Z", "utc_arrival": "2023-04-14T19:45:00.000Z", "local_departure": "2023-04-14T18:25:00.000Z", "utc_departure": "2023-04-14T16:25:00.000Z"}, {"id": "0a220b774c080000c0858f1c_0", "combination_id": "0a220b774c080000c0858f1c", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "BREG", "fare_category": "M", "fare_classes": "B", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-17T23:45:00.000Z", "utc_arrival": "2023-04-17T21:45:00.000Z", "local_departure": "2023-04-17T20:30:00.000Z", "utc_departure": "2023-04-17T18:30:00.000Z"}], "booking_token": "El3FBBHJJPC18JkVuIft6K9J79-NLTEVKbTDO-QLRgxzibajyZE7f0E-ueSVdSw8-GlJb2mFJ5xwW3hmh4tRtoN9WDNFRh88Zf49coaW-HfuXlIGPSSlgp3qulbOEBCU7dBnwxXpn6t_Hi8w2URQpRXTt-9pvawpQv1CAvbFeq8cF058pxuYugqOZnLlqId4_yyko1npb7_cuEdM6CyaQkrI2hXt1L1Z-EYdH4EBp8q5ZwQ14rJ7zSOPJ0XLUIl0pKaOMzeZYxKr0Rjel6Wr5ctn3h0cSt0g3ROAk9IzSzKYc4O4PQYBwicfKhmu0qvucqmWpfkVjzSnGUKNG89iNIHyZNj_LB76ZrPFPuKyx4HJKTcCM5-TOLK9JrJmB1QDA9ZTw0S8yJFTW65fjadGBlO6wCp4fJHdES8s_P9wOFFcV3yFovuSqXhWyQKTL-G9eAUBtms92TZrM_kCN8SP1KR8EFYxnyymmETHNkfnaix259EQNHGOALzMjxiT6V82b9YEXWRT7_eTqucT_RS2rPQ1U4MtaknKVTIkugsFs2dWeRD_WiVrXRm7MVZqXzuaFp3SDt9RLSSWUktcJ0VaxieM9k0HRn5_D6if5z86AweBbKRrrdpn8ium8Wv_bo5G_NYif0xGFAJFNyLzgkSpT3FEoivV9LmCz2ahZQ3ky4d9Hc_YxMA9p6Jg9EYrODGCLciChMkW9ip2HpiK4IgnZzhMVm04WpyUzle9XR4NCGip1Uiv1mvinH7fZM_BWj4fvSIPfMGZZmfrh8_9rpdaIYg==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c05000004bc72da_0%7C0a220b774c080000c0858f1c_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=El3FBBHJJPC18JkVuIft6K9J79-NLTEVKbTDO-QLRgxzibajyZE7f0E-ueSVdSw8-GlJb2mFJ5xwW3hmh4tRtoN9WDNFRh88Zf49coaW-HfuXlIGPSSlgp3qulbOEBCU7dBnwxXpn6t_Hi8w2URQpRXTt-9pvawpQv1CAvbFeq8cF058pxuYugqOZnLlqId4_yyko1npb7_cuEdM6CyaQkrI2hXt1L1Z-EYdH4EBp8q5ZwQ14rJ7zSOPJ0XLUIl0pKaOMzeZYxKr0Rjel6Wr5ctn3h0cSt0g3ROAk9IzSzKYc4O4PQYBwicfKhmu0qvucqmWpfkVjzSnGUKNG89iNIHyZNj_LB76ZrPFPuKyx4HJKTcCM5-TOLK9JrJmB1QDA9ZTw0S8yJFTW65fjadGBlO6wCp4fJHdES8s_P9wOFFcV3yFovuSqXhWyQKTL-G9eAUBtms92TZrM_kCN8SP1KR8EFYxnyymmETHNkfnaix259EQNHGOALzMjxiT6V82b9YEXWRT7_eTqucT_RS2rPQ1U4MtaknKVTIkugsFs2dWeRD_WiVrXRm7MVZqXzuaFp3SDt9RLSSWUktcJ0VaxieM9k0HRn5_D6if5z86AweBbKRrrdpn8ium8Wv_bo5G_NYif0xGFAJFNyLzgkSpT3FEoivV9LmCz2ahZQ3ky4d9Hc_YxMA9p6Jg9EYrODGCLciChMkW9ip2HpiK4IgnZzhMVm04WpyUzle9XR4NCGip1Uiv1mvinH7fZM_BWj4fvSIPfMGZZmfrh8_9rpdaIYg==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-04-14T21:45:00.000Z", "utc_arrival": "2023-04-14T19:45:00.000Z", "local_departure": "2023-04-14T18:25:00.000Z", "utc_departure": "2023-04-14T16:25:00.000Z"}, {"id": "0b770a224c280000d84fb6b2_0|0a220b774c2b00000a3f7587_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 726.898324, "distance": 1975.87, "duration": {"departure": 12600, "return": 11400, "total": 24000}, "price": 218596.3712, "conversion": {"EUR": 572.232044, "HUF": 218596.3712}, "fare": {"adults": 109298.19, "children": 109298.19, "infants": 109298.19}, "bags_price": {"1": 90.804, "2": 181.622}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 3}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224c280000d84fb6b2_0", "combination_id": "0b770a224c280000d84fb6b2", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-19T19:45:00.000Z", "utc_arrival": "2023-05-19T17:45:00.000Z", "local_departure": "2023-05-19T16:15:00.000Z", "utc_departure": "2023-05-19T14:15:00.000Z"}, {"id": "0a220b774c2b00000a3f7587_0", "combination_id": "0a220b774c2b00000a3f7587", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-22T10:15:00.000Z", "utc_arrival": "2023-05-22T08:15:00.000Z", "local_departure": "2023-05-22T07:05:00.000Z", "utc_departure": "2023-05-22T05:05:00.000Z"}], "booking_token": "Eh52YqyymmLVLNstm5nFkvJ5JoDn5xpie1wntjHo9lgv6kPh0gtriqZ4bNQ1X9VnkBI_8Mbg7YgY0PpFED81FPtbcxfhifQvxfh6IuWHzk9AgZJJ0Bs0nFzwqdPbP6ZudP-on-IAatsJ2mcq4fSzto9ALAjOHgSedDzhGU5u8CwwRdbvK9nRtLVpvP6LWu3aBIdFyT--iztiMut3rZTZGfu2vrazCtoiGtYqHXyByi1fIigp_Jzrr2L6UL9SLjpkigfLWc3g8jMex29TG1Lj39h3cidxJACI3bOVXaTT9nKUuWx7HhEyGX7xp0Wop1Yu7w5Fc0FLgAVbRc_zOcPyypB1ARFrfRfv2sydF51y3TGGwA7D7GXZECZQJLA3eyHz0nHKJibLbZLanbzJeYDCEUCtvjvgpv18vO5hoxSLZhoUmokJgCPtlRL4q8HhjCHCPv2Y-8H3LQiyRhEcGZdSIKIrp_eWMQ6LP-V737rOnWJW9cRKJKxsXtoX9dUgAcur-diP1txxgCKUJIqVei9ZnB17SFRH0rJOJbf7cVdJK2iYK5EBtTFETPtkfW2gwbtMweLmetBKXtgKxeg5glqm-FjUKmMMJIQy0j0vI-Ob4zT8uYyZWMpTP8jikJurIA1xH2ixSVmrE8IQ08Kl1T-ykYIQf9HMLmIK4Y5jBdpK4muXGSR9Y5N4ffP3FMFy6eVmUm7Q5tc1qIPsQgkqv2HNSAE8wYfphicqddLVH737-11IJsNXemH7Is54dvN5Nh5-gj1b1v_lQmtYMxpiCZkLSnTJ83fkInK7FI3FAAXnI17Q=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c280000d84fb6b2_0%7C0a220b774c2b00000a3f7587_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=Eh52YqyymmLVLNstm5nFkvJ5JoDn5xpie1wntjHo9lgv6kPh0gtriqZ4bNQ1X9VnkBI_8Mbg7YgY0PpFED81FPtbcxfhifQvxfh6IuWHzk9AgZJJ0Bs0nFzwqdPbP6ZudP-on-IAatsJ2mcq4fSzto9ALAjOHgSedDzhGU5u8CwwRdbvK9nRtLVpvP6LWu3aBIdFyT--iztiMut3rZTZGfu2vrazCtoiGtYqHXyByi1fIigp_Jzrr2L6UL9SLjpkigfLWc3g8jMex29TG1Lj39h3cidxJACI3bOVXaTT9nKUuWx7HhEyGX7xp0Wop1Yu7w5Fc0FLgAVbRc_zOcPyypB1ARFrfRfv2sydF51y3TGGwA7D7GXZECZQJLA3eyHz0nHKJibLbZLanbzJeYDCEUCtvjvgpv18vO5hoxSLZhoUmokJgCPtlRL4q8HhjCHCPv2Y-8H3LQiyRhEcGZdSIKIrp_eWMQ6LP-V737rOnWJW9cRKJKxsXtoX9dUgAcur-diP1txxgCKUJIqVei9ZnB17SFRH0rJOJbf7cVdJK2iYK5EBtTFETPtkfW2gwbtMweLmetBKXtgKxeg5glqm-FjUKmMMJIQy0j0vI-Ob4zT8uYyZWMpTP8jikJurIA1xH2ixSVmrE8IQ08Kl1T-ykYIQf9HMLmIK4Y5jBdpK4muXGSR9Y5N4ffP3FMFy6eVmUm7Q5tc1qIPsQgkqv2HNSAE8wYfphicqddLVH737-11IJsNXemH7Is54dvN5Nh5-gj1b1v_lQmtYMxpiCZkLSnTJ83fkInK7FI3FAAXnI17Q=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-19T19:45:00.000Z", "utc_arrival": "2023-05-19T17:45:00.000Z", "local_departure": "2023-05-19T16:15:00.000Z", "utc_departure": "2023-05-19T14:15:00.000Z"}, {"id": "0b770a224c1b000010a8e402_0|0a220b774c1e00004eb45e85_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 725.444692, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 219059.7558, "conversion": {"EUR": 573.445072, "HUF": 219059.7558}, "fare": {"adults": 109529.88, "children": 114041.1, "infants": 114041.1}, "bags_price": {"1": 73.822, "2": 147.644}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 6}, "airlines": ["FR"], "route": [{"id": "0b770a224c1b000010a8e402_0", "combination_id": "0b770a224c1b000010a8e402", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-06T13:25:00.000Z", "utc_arrival": "2023-05-06T11:25:00.000Z", "local_departure": "2023-05-06T10:05:00.000Z", "utc_departure": "2023-05-06T08:05:00.000Z"}, {"id": "0a220b774c1e00004eb45e85_0", "combination_id": "0a220b774c1e00004eb45e85", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-09T14:05:00.000Z", "utc_arrival": "2023-05-09T12:05:00.000Z", "local_departure": "2023-05-09T10:55:00.000Z", "utc_departure": "2023-05-09T08:55:00.000Z"}], "booking_token": "E8IPKZVkfUaMFFm26GjKgX1F7eTvOYFe4bda2110sFAheM-F5bm-cSOwC3x93xSKplxFJgFxfhET2soRlBfTWlXGBa019KjPQjqF23c0pqWpAVJnpO8C1_bdXj4id-2PN5bKTqOQVxnh9MN2mIE-41XrKctVxYfovPrnCiorztaBa5Rw032oJ1as0gTtNz5cB-M0xY5QQpIYNpQRtj7LkA7A8O5xCF6YpANimhyIZ6hvwQl7Ydmzwa5sUzMMQnAclJgJe8VQkqedT-KLcCGk_xFIcyaKmy7fPUqu5NRqCWyZcF5HIwMAZ4vP89N_8eUu12opJVOwNiAgo47XRUHc7uR0Iqwxyn3XX-kkYkoGb-aQhAiOv_aU0jnSjIy9RAQCmYLHQQackcPLrGphCUR8Hk6qo7ENISoLhkQLkYKc2at99QWk9_3iA1yezNhvU8cL2rHjnXR-7Z90hWHdgji5kQ_XWcVE3svk79b7t75fAzrqs92d-2LM_qxE98HNqTGHbSIWqsMREbGXTtI4soppmC6pzwoXOcb4P4dolSkmvQ1h1GtGs2L83AUzlfiDCH84OAn-dGsb35aQbKHkGkCYtCMZHfqFO5uWR0aN9R46mO31wL_-Xe7dUzWVjtf2B0xnNKhwrfP-rny6DeDNpzmQ1sVQ6y-dnZmfIDKYjjVG44w_iujAq3Y0UpYem_HieiXoQcx1BtKPBwxEYNF4vkFeFcNUF-0Z9ag_XPm-yNLHLNWM=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c1b000010a8e402_0%7C0a220b774c1e00004eb45e85_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=E8IPKZVkfUaMFFm26GjKgX1F7eTvOYFe4bda2110sFAheM-F5bm-cSOwC3x93xSKplxFJgFxfhET2soRlBfTWlXGBa019KjPQjqF23c0pqWpAVJnpO8C1_bdXj4id-2PN5bKTqOQVxnh9MN2mIE-41XrKctVxYfovPrnCiorztaBa5Rw032oJ1as0gTtNz5cB-M0xY5QQpIYNpQRtj7LkA7A8O5xCF6YpANimhyIZ6hvwQl7Ydmzwa5sUzMMQnAclJgJe8VQkqedT-KLcCGk_xFIcyaKmy7fPUqu5NRqCWyZcF5HIwMAZ4vP89N_8eUu12opJVOwNiAgo47XRUHc7uR0Iqwxyn3XX-kkYkoGb-aQhAiOv_aU0jnSjIy9RAQCmYLHQQackcPLrGphCUR8Hk6qo7ENISoLhkQLkYKc2at99QWk9_3iA1yezNhvU8cL2rHjnXR-7Z90hWHdgji5kQ_XWcVE3svk79b7t75fAzrqs92d-2LM_qxE98HNqTGHbSIWqsMREbGXTtI4soppmC6pzwoXOcb4P4dolSkmvQ1h1GtGs2L83AUzlfiDCH84OAn-dGsb35aQbKHkGkCYtCMZHfqFO5uWR0aN9R46mO31wL_-Xe7dUzWVjtf2B0xnNKhwrfP-rny6DeDNpzmQ1sVQ6y-dnZmfIDKYjjVG44w_iujAq3Y0UpYem_HieiXoQcx1BtKPBwxEYNF4vkFeFcNUF-0Z9ag_XPm-yNLHLNWM=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-06T13:25:00.000Z", "utc_arrival": "2023-05-06T11:25:00.000Z", "local_departure": "2023-05-06T10:05:00.000Z", "utc_departure": "2023-05-06T08:05:00.000Z"}, {"id": "0b770a224bee000038feff2a_0|0a220b774bf10000f0b20103_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 727.992715, "distance": 1975.87, "duration": {"departure": 12000, "return": 11700, "total": 23700}, "price": 219523.7764, "conversion": {"EUR": 574.659765, "HUF": 219523.7764}, "fare": {"adults": 109761.89, "children": 109761.89, "infants": 109761.89}, "bags_price": {"1": 87.906, "2": 175.812}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 6}, "airlines": ["FR"], "route": [{"id": "0b770a224bee000038feff2a_0", "combination_id": "0b770a224bee000038feff2a", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-03-22T23:20:00.000Z", "utc_arrival": "2023-03-22T22:20:00.000Z", "local_departure": "2023-03-22T20:00:00.000Z", "utc_departure": "2023-03-22T19:00:00.000Z"}, {"id": "0a220b774bf10000f0b20103_0", "combination_id": "0a220b774bf10000f0b20103", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6709, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-03-25T18:05:00.000Z", "utc_arrival": "2023-03-25T17:05:00.000Z", "local_departure": "2023-03-25T14:50:00.000Z", "utc_departure": "2023-03-25T13:50:00.000Z"}], "booking_token": "EX6K01ZF8yZNmZYxGv5hMyJiH28zI-TDkrSD4uEmH0OCjC6YnWs7VqdPEd5yEKS2Bs3N60OJS-Xkp0pPXYr9sfWtt_QGbTZW8fQ1G4vfk2ZjKvprUar9kUM_G74OpE4Kgl9xAnvDTpDOHhyj3cl3vm8ZGLSOR3SPNkpZKtE-5F1BdF2wGLp1HSnF_0hyZpVXZMyeZwGQ5yttAb6rcIj9mzuXq8Q_vzrWmd23bYMjFSilElBBCgPBdUYoXsMgzlN3ryCFal-uUKURD4G8tplEIS5-GSIsZY1EfmLDW-RcNOYOV9wAMckVWOd2Gz9v0u9HmYJai0ea4bQk4A6MO24fhh91ZDzflTyBb02ZyF9Xw7kPXA1_pE4__UVkvVxwPhziC1idZBEgXKDRjV3SV8op5F2gZOUaATDKRm2_WAafj7PRRB6a3fPefJRMUgtsz3AluY54eQYqnofBlDuXb9WzZFYX8E5XzPLQdw3uyS37eQmnk-NNGjGCeLO_L8-fOBj6JbOxiaQtd8Ub01w-2CFJtTUV38VrgeMEPf-9uzeUC19SeL_mUjIoMer7UoGWqx4G2SEjGxo2k8FzQmcjz77uxFY6hpIVCqy77ntjm8WgW7sG-5VdU7NwV1T2tWP43ZvlJKpHM0whCBYZrTb0_1SPOCHmEnD57lwhYaeqPtnes6Kh_IHKI1eMju0cc5I9cTPvTj1vEZZ6eFV7Va2bM4esXW7zcKIvNkBIwZ2AAOBRl3B6A3xgKHwgWvFc3yMzBHvov", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224bee000038feff2a_0%7C0a220b774bf10000f0b20103_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EX6K01ZF8yZNmZYxGv5hMyJiH28zI-TDkrSD4uEmH0OCjC6YnWs7VqdPEd5yEKS2Bs3N60OJS-Xkp0pPXYr9sfWtt_QGbTZW8fQ1G4vfk2ZjKvprUar9kUM_G74OpE4Kgl9xAnvDTpDOHhyj3cl3vm8ZGLSOR3SPNkpZKtE-5F1BdF2wGLp1HSnF_0hyZpVXZMyeZwGQ5yttAb6rcIj9mzuXq8Q_vzrWmd23bYMjFSilElBBCgPBdUYoXsMgzlN3ryCFal-uUKURD4G8tplEIS5-GSIsZY1EfmLDW-RcNOYOV9wAMckVWOd2Gz9v0u9HmYJai0ea4bQk4A6MO24fhh91ZDzflTyBb02ZyF9Xw7kPXA1_pE4__UVkvVxwPhziC1idZBEgXKDRjV3SV8op5F2gZOUaATDKRm2_WAafj7PRRB6a3fPefJRMUgtsz3AluY54eQYqnofBlDuXb9WzZFYX8E5XzPLQdw3uyS37eQmnk-NNGjGCeLO_L8-fOBj6JbOxiaQtd8Ub01w-2CFJtTUV38VrgeMEPf-9uzeUC19SeL_mUjIoMer7UoGWqx4G2SEjGxo2k8FzQmcjz77uxFY6hpIVCqy77ntjm8WgW7sG-5VdU7NwV1T2tWP43ZvlJKpHM0whCBYZrTb0_1SPOCHmEnD57lwhYaeqPtnes6Kh_IHKI1eMju0cc5I9cTPvTj1vEZZ6eFV7Va2bM4esXW7zcKIvNkBIwZ2AAOBRl3B6A3xgKHwgWvFc3yMzBHvov", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-03-22T23:20:00.000Z", "utc_arrival": "2023-03-22T22:20:00.000Z", "local_departure": "2023-03-22T20:00:00.000Z", "utc_departure": "2023-03-22T19:00:00.000Z"}, {"id": "0b770a224c200000df962b2d_0|0a220b774c2400009a975815_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 725.517517, "distance": 1975.87, "duration": {"departure": 11700, "return": 11400, "total": 23100}, "price": 219596.9162, "conversion": {"EUR": 574.851227, "HUF": 219596.9162}, "fare": {"adults": 109798.46, "children": 109798.46, "infants": 109798.46}, "bags_price": {"1": 74.886, "2": 159.572}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 158, "hold_height": 52, "hold_length": 78, "hold_weight": 20, "hold_width": 28, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 3, "personal_item_width": 15}, "availability": {"seats": 4}, "airlines": ["FR", "IB"], "route": [{"id": "0b770a224c200000df962b2d_0", "combination_id": "0b770a224c200000df962b2d", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "IB", "flight_no": 3279, "operating_carrier": "IB", "operating_flight_no": "3279", "fare_basis": "NZNNAOB4", "fare_category": "M", "fare_classes": "N", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-11T18:50:00.000Z", "utc_arrival": "2023-05-11T16:50:00.000Z", "local_departure": "2023-05-11T15:35:00.000Z", "utc_departure": "2023-05-11T13:35:00.000Z"}, {"id": "0a220b774c2400009a975815_0", "combination_id": "0a220b774c2400009a975815", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-15T10:15:00.000Z", "utc_arrival": "2023-05-15T08:15:00.000Z", "local_departure": "2023-05-15T07:05:00.000Z", "utc_departure": "2023-05-15T05:05:00.000Z"}], "booking_token": "ERjQAiO-gxI9mbvnYw0baiiO_-jsLZrfCavUZaMiQMPh1q_04anDOJPtIO7mO9QGSKoKeHLyMplPh_-G8hcJ2OncGvzBfivNnT3XZkDU0PBCApP60YtRCxmS0mCXiYGKj2jlI53XpTBWInfxyxx70aOqlZY3yi8wuaEtSR1AJp_t19AqDpXlkeQcMNdsrL8NqQZTl_o0t6Yj_CdUHHUe1Pj0XTYnMCJorB4O6jPLslFlCqgKUWVlicvBEmEK_xlaK1C4vqUIK5kwcMI1nkBu1yN9_x8OjP1BBffUK5gADu937ygxrDUtU0FTcouuv0RIJTqVucaYLdVSDAssoGP_VPKqqbqjwQkSrvlOKFmX-XuCouyMMDToEQhUqDKuMnCNBsgbwuRVvFCkxTSCCGQ5iB6w1g-iOTakGDrFZnL6bO_rvocG0F52H5PgmtWru7_BgUjC75CpXcVwdDdKXLX3KBZtuxCa9w3i6SFNPcm4FouXYNUHft0wPDTCuC-xx1VPQSqFUG9QgdEnyHYWuedDDlvy9_iuRKWnWmREeZXzamNdoKecBs6OIDQ989946kx5V8GXluGYokQoNe6pmcyK9jpMcNQaoDvd6iItO-kdL2LRVN4wLixH8vjJQqAOvW9abh7rzme4ZPC6a1eYIDu8F9CIuEpmyAX-etSiBbjVa0hVFU0YEb9zS_yuTvrSA_uuByVakywhzx10wf6clajswpNFuDaqNVe5EtMoIkpQpDxe6PrCqmThM5Q6Y8Yqg9fDksRwHecM7QKKMS7kelOT74YCSExWgaOaNEoki9V5s1HM=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c200000df962b2d_0%7C0a220b774c2400009a975815_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=ERjQAiO-gxI9mbvnYw0baiiO_-jsLZrfCavUZaMiQMPh1q_04anDOJPtIO7mO9QGSKoKeHLyMplPh_-G8hcJ2OncGvzBfivNnT3XZkDU0PBCApP60YtRCxmS0mCXiYGKj2jlI53XpTBWInfxyxx70aOqlZY3yi8wuaEtSR1AJp_t19AqDpXlkeQcMNdsrL8NqQZTl_o0t6Yj_CdUHHUe1Pj0XTYnMCJorB4O6jPLslFlCqgKUWVlicvBEmEK_xlaK1C4vqUIK5kwcMI1nkBu1yN9_x8OjP1BBffUK5gADu937ygxrDUtU0FTcouuv0RIJTqVucaYLdVSDAssoGP_VPKqqbqjwQkSrvlOKFmX-XuCouyMMDToEQhUqDKuMnCNBsgbwuRVvFCkxTSCCGQ5iB6w1g-iOTakGDrFZnL6bO_rvocG0F52H5PgmtWru7_BgUjC75CpXcVwdDdKXLX3KBZtuxCa9w3i6SFNPcm4FouXYNUHft0wPDTCuC-xx1VPQSqFUG9QgdEnyHYWuedDDlvy9_iuRKWnWmREeZXzamNdoKecBs6OIDQ989946kx5V8GXluGYokQoNe6pmcyK9jpMcNQaoDvd6iItO-kdL2LRVN4wLixH8vjJQqAOvW9abh7rzme4ZPC6a1eYIDu8F9CIuEpmyAX-etSiBbjVa0hVFU0YEb9zS_yuTvrSA_uuByVakywhzx10wf6clajswpNFuDaqNVe5EtMoIkpQpDxe6PrCqmThM5Q6Y8Yqg9fDksRwHecM7QKKMS7kelOT74YCSExWgaOaNEoki9V5s1HM=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-11T18:50:00.000Z", "utc_arrival": "2023-05-11T16:50:00.000Z", "local_departure": "2023-05-11T15:35:00.000Z", "utc_departure": "2023-05-11T13:35:00.000Z"}, {"id": "0b770a224c3a0000c54ce2f2_0|0a220b774c3e00005dc9ddc7_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 727.393899, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 219804.3656, "conversion": {"EUR": 575.394279, "HUF": 219804.3656}, "fare": {"adults": 109902.18, "children": 109902.18, "infants": 109902.18}, "bags_price": {"1": 75.068, "2": 159.95}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 158, "hold_height": 52, "hold_length": 78, "hold_weight": 20, "hold_width": 28, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 3, "personal_item_width": 15}, "availability": {"seats": 5}, "airlines": ["FR", "VY"], "route": [{"id": "0b770a224c3a0000c54ce2f2_0", "combination_id": "0b770a224c3a0000c54ce2f2", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-06T10:15:00.000Z", "utc_arrival": "2023-06-06T08:15:00.000Z", "local_departure": "2023-06-06T06:55:00.000Z", "utc_departure": "2023-06-06T04:55:00.000Z"}, {"id": "0a220b774c3e00005dc9ddc7_0", "combination_id": "0a220b774c3e00005dc9ddc7", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "VY", "flight_no": 5192, "operating_carrier": "IB", "operating_flight_no": "3278", "fare_basis": "ZSBBHJA", "fare_category": "M", "fare_classes": "Z", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": "32S", "vehicle_type": "aircraft", "local_arrival": "2023-06-10T14:55:00.000Z", "utc_arrival": "2023-06-10T12:55:00.000Z", "local_departure": "2023-06-10T11:45:00.000Z", "utc_departure": "2023-06-10T09:45:00.000Z"}], "booking_token": "E0K7I_IrNT1UWUuiQfo2bwc8elZx3mOhA54NxUpCDcRB8M05HNSWxdDTOnCM9Sdjd8-ZDG8AP131jz701ltYBE8dCSIJTgt1ZBFcuSxgq-D0HbIMvcrE-RiAmIHwcupMZafSsFGK3Yru2BFf90okYLds3bWKwBnu6sEp4VgttwvAegUJfbeFC_LEiDR8f36VfKeGs7mcgREf26cGd3CXj9Fkr9QJGJK_aRhG8Nn6hAUDE9i-kzIrmmmQoBZs9QH0J1MvPo1-zN-PPlF5YLW-xgM13li9b7jX5nteMWxHekdscgg-wsZRDfylb34UBz8wcj6DKFNIsJ2XpGOMVP3OXS1SpbkxS0K8iD0AJXnLnKfIDJdDIZyrIAvf8_rLylTolCCLLV0H83pi1fvEqnxobGnOeqM-sSPzbjdJUgpgOZe-f-EIB8nVWW7GD0jANtrDcUz7B534y8U8xYYYzjoVMY5FWJZgb0k8npvucAdzI6DzQ9pf4x6nVAAwMuAEsk-6Un5MbTefkRDboxxg7lc2o2BeztvumP4TzBAbSwp2nSU2rE9TOpeNw0czkXgHzB9OaRr85iCsafC9JuyESpNC802QW20mecKzINFw78l4YgO3RTOVKlWz4UTBZfb8xHcjhJ_oxrRyO90Gfn_LHy7hgqGCgZRtoLKQOF58vN2XHR_ymuKNP8P4hzl_gqk_Ffjd93qCrdQmGQ37IHlx2lOBZ7ffBQk4P-oLM9GqzXH-qSHgjbHq195QJaiU9UZj89MN1", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c3a0000c54ce2f2_0%7C0a220b774c3e00005dc9ddc7_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=E0K7I_IrNT1UWUuiQfo2bwc8elZx3mOhA54NxUpCDcRB8M05HNSWxdDTOnCM9Sdjd8-ZDG8AP131jz701ltYBE8dCSIJTgt1ZBFcuSxgq-D0HbIMvcrE-RiAmIHwcupMZafSsFGK3Yru2BFf90okYLds3bWKwBnu6sEp4VgttwvAegUJfbeFC_LEiDR8f36VfKeGs7mcgREf26cGd3CXj9Fkr9QJGJK_aRhG8Nn6hAUDE9i-kzIrmmmQoBZs9QH0J1MvPo1-zN-PPlF5YLW-xgM13li9b7jX5nteMWxHekdscgg-wsZRDfylb34UBz8wcj6DKFNIsJ2XpGOMVP3OXS1SpbkxS0K8iD0AJXnLnKfIDJdDIZyrIAvf8_rLylTolCCLLV0H83pi1fvEqnxobGnOeqM-sSPzbjdJUgpgOZe-f-EIB8nVWW7GD0jANtrDcUz7B534y8U8xYYYzjoVMY5FWJZgb0k8npvucAdzI6DzQ9pf4x6nVAAwMuAEsk-6Un5MbTefkRDboxxg7lc2o2BeztvumP4TzBAbSwp2nSU2rE9TOpeNw0czkXgHzB9OaRr85iCsafC9JuyESpNC802QW20mecKzINFw78l4YgO3RTOVKlWz4UTBZfb8xHcjhJ_oxrRyO90Gfn_LHy7hgqGCgZRtoLKQOF58vN2XHR_ymuKNP8P4hzl_gqk_Ffjd93qCrdQmGQ37IHlx2lOBZ7ffBQk4P-oLM9GqzXH-qSHgjbHq195QJaiU9UZj89MN1", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-06T10:15:00.000Z", "utc_arrival": "2023-06-06T08:15:00.000Z", "local_departure": "2023-06-06T06:55:00.000Z", "utc_departure": "2023-06-06T04:55:00.000Z"}, {"id": "0b770a224c40000061fa8349_0|0a220b774c430000391b6c3b_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 729.876233, "distance": 1975.87, "duration": {"departure": 12000, "return": 11700, "total": 23700}, "price": 220243.2926, "conversion": {"EUR": 576.543283, "HUF": 220243.2926}, "fare": {"adults": 110121.65, "children": 110121.65, "infants": 110121.65}, "bags_price": {"1": 99.568, "2": 199.122}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 5}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224c40000061fa8349_0", "combination_id": "0b770a224c40000061fa8349", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-12T14:00:00.000Z", "utc_arrival": "2023-06-12T12:00:00.000Z", "local_departure": "2023-06-12T10:40:00.000Z", "utc_departure": "2023-06-12T08:40:00.000Z"}, {"id": "0a220b774c430000391b6c3b_0", "combination_id": "0a220b774c430000391b6c3b", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "JREG", "fare_category": "M", "fare_classes": "J", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-16T01:15:00.000Z", "utc_arrival": "2023-06-15T23:15:00.000Z", "local_departure": "2023-06-15T22:00:00.000Z", "utc_departure": "2023-06-15T20:00:00.000Z"}], "booking_token": "E9dFKyZuAe6vdNKWb3-khq740hRUIhsaxmOAxQKfU2axOTB2OWE7MonVc33SaI_hkaRx7lw3Af_TpWOED7oaoE9KekPUDkb6uOftuFGdZvBYhjzvgD_lbCg-YVa89a4O6PH55ybyBNyNy0CYrYYBKMQde8-JR4OsErDgV6d_jR67Z0L8iWXTE_0U01Bm3oMyCOMLkaIkr6x4JAVQ5fvTUhTTnI1ASrfdffm1iH50yzk2hS-L-fYQ6xNBzRuUaFvHKKbDLJwbppqyhiGXBuMf_WBpvN2t-UnAwxdDnjXQuseFM60sH8-fK99x3pgaxWyGDpiBVNiwRUuoKCxFbKHT5GFBIYOZbedkxa0XqfBWN1AFP0fd9IjPpCwYmYjgcRAuNlwZydu6nDAvg4BfiGP4yU4ApgyJUEVV_z30OuaYMFhS9jiT3XDhGRS4h3LnGWzeKjn8VCu_mVPGG0FBN54UQDcNHtUnpyUiALqjS95G5cWrKzNKPzzacFXhiFdLsph5p9zOPQtdjUs4ZodL8Z3tIhMxgRNGUG9xtERfyBckw_MB5zInPccLNYEUSlHuRs9pvczTMmga44Kdur0aWE_N6JfM5NoaKrXsSCiJn6CdBsmnznRGWkPpcNQh7Vx9TUkGM-tNFOim1R8FSRiIZ6WI8kjtop6Y98ghMevqhAKVjrj2NysWGmLK_bNJvyqNXogl4fSf47JY6myvceEoke_jUWL1qJaw22evzvcl0Lj6QLAsY6YQkqqhjMmgTHlBACiofRvC1shP6FCozsV1wW0RYFQ==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c40000061fa8349_0%7C0a220b774c430000391b6c3b_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=E9dFKyZuAe6vdNKWb3-khq740hRUIhsaxmOAxQKfU2axOTB2OWE7MonVc33SaI_hkaRx7lw3Af_TpWOED7oaoE9KekPUDkb6uOftuFGdZvBYhjzvgD_lbCg-YVa89a4O6PH55ybyBNyNy0CYrYYBKMQde8-JR4OsErDgV6d_jR67Z0L8iWXTE_0U01Bm3oMyCOMLkaIkr6x4JAVQ5fvTUhTTnI1ASrfdffm1iH50yzk2hS-L-fYQ6xNBzRuUaFvHKKbDLJwbppqyhiGXBuMf_WBpvN2t-UnAwxdDnjXQuseFM60sH8-fK99x3pgaxWyGDpiBVNiwRUuoKCxFbKHT5GFBIYOZbedkxa0XqfBWN1AFP0fd9IjPpCwYmYjgcRAuNlwZydu6nDAvg4BfiGP4yU4ApgyJUEVV_z30OuaYMFhS9jiT3XDhGRS4h3LnGWzeKjn8VCu_mVPGG0FBN54UQDcNHtUnpyUiALqjS95G5cWrKzNKPzzacFXhiFdLsph5p9zOPQtdjUs4ZodL8Z3tIhMxgRNGUG9xtERfyBckw_MB5zInPccLNYEUSlHuRs9pvczTMmga44Kdur0aWE_N6JfM5NoaKrXsSCiJn6CdBsmnznRGWkPpcNQh7Vx9TUkGM-tNFOim1R8FSRiIZ6WI8kjtop6Y98ghMevqhAKVjrj2NysWGmLK_bNJvyqNXogl4fSf47JY6myvceEoke_jUWL1qJaw22evzvcl0Lj6QLAsY6YQkqqhjMmgTHlBACiofRvC1shP6FCozsV1wW0RYFQ==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-12T14:00:00.000Z", "utc_arrival": "2023-06-12T12:00:00.000Z", "local_departure": "2023-06-12T10:40:00.000Z", "utc_departure": "2023-06-12T08:40:00.000Z"}, {"id": "0b770a224c050000101ee0e9_0|0a220b774c080000c0858f1c_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 733.282077, "distance": 1975.87, "duration": {"departure": 12600, "return": 11700, "total": 24300}, "price": 220525.6657, "conversion": {"EUR": 577.282467, "HUF": 220525.6657}, "fare": {"adults": 110262.83, "children": 110262.83, "infants": 110262.83}, "bags_price": {"1": 146.986, "2": 293.958}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 439, "hold_height": 149, "hold_length": 171, "hold_weight": 20, "hold_width": 119, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 2}, "airlines": ["W6"], "route": [{"id": "0b770a224c050000101ee0e9_0", "combination_id": "0b770a224c050000101ee0e9", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-14T19:45:00.000Z", "utc_arrival": "2023-04-14T17:45:00.000Z", "local_departure": "2023-04-14T16:15:00.000Z", "utc_departure": "2023-04-14T14:15:00.000Z"}, {"id": "0a220b774c080000c0858f1c_0", "combination_id": "0a220b774c080000c0858f1c", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "BREG", "fare_category": "M", "fare_classes": "B", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-17T23:45:00.000Z", "utc_arrival": "2023-04-17T21:45:00.000Z", "local_departure": "2023-04-17T20:30:00.000Z", "utc_departure": "2023-04-17T18:30:00.000Z"}], "booking_token": "EfaV9cyBkX7a_TcLvenxYLjDVcgGT74QEZYmoupAD2N5vKwWkik-F54AH2yTCa8w3I7pgBovCY_CJfK4_QGjuJyK9fb7hhRukkdNHv8466s1eGMFCzOzF9r_ZwjXWg4kk2EfCT0IswEtO90GacwdGtZWGWvbBh3w2Bd3uu3agjenhHiZZBF0tNYGi-EjfnHON6tcrFmWfvAbBJBY3AnzSzbGzDFp4uW7rgJjbYcLcv8du93wVjdmcmbzdEfphUE5KSF9aNauIdkf2vGHcuzO9OW8lQsYXSq6umijm5FmDTnaAdeHsga-6ax5wrAYwYTGj9rZNRvKpVEd2Fc-x8tFDPY_HFtKabu1Zu3hEsKLBhyJnLJbcSWRvUX-yPXAtbJgIIeFinNFyyoJFRnsHmv-EK9nvWcFqX9CFy2FXQyD9HIqXR0vNtKVQVRpVshnU0z223TsDckrHfz7QQuBg4zyaZLqUAO61barMS9DbqZL22UCn0v5oe2f5V3nkCbfo8AALaeCCzLMETnyJ2fcmpJ0-DTkXmyiY_S05-2K_5TObRMbfmlGokg8xDDrtOyq9A5uZtJVqNusoQavQDFGv4-cmJofcbVHqOdDbqTBiMUvfuflu-wtm4pKRBs4bLXzTY3sE9OUPZBo9ZbEIoGLW7KQOmHEoMobDzTBz5MgiiVSd1YJOuxZtB_aHeR21sEy1BN6TkaUMoyidES9SOS_386Sejn4C4vRgAkMmGxaTD5WvT_Cem-H46IZENvLbzIjdoUblA2HfnfQ3Eg9gOblZlE3_MUql6We-giWM6J6B2y5aCyQ=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c050000101ee0e9_0%7C0a220b774c080000c0858f1c_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EfaV9cyBkX7a_TcLvenxYLjDVcgGT74QEZYmoupAD2N5vKwWkik-F54AH2yTCa8w3I7pgBovCY_CJfK4_QGjuJyK9fb7hhRukkdNHv8466s1eGMFCzOzF9r_ZwjXWg4kk2EfCT0IswEtO90GacwdGtZWGWvbBh3w2Bd3uu3agjenhHiZZBF0tNYGi-EjfnHON6tcrFmWfvAbBJBY3AnzSzbGzDFp4uW7rgJjbYcLcv8du93wVjdmcmbzdEfphUE5KSF9aNauIdkf2vGHcuzO9OW8lQsYXSq6umijm5FmDTnaAdeHsga-6ax5wrAYwYTGj9rZNRvKpVEd2Fc-x8tFDPY_HFtKabu1Zu3hEsKLBhyJnLJbcSWRvUX-yPXAtbJgIIeFinNFyyoJFRnsHmv-EK9nvWcFqX9CFy2FXQyD9HIqXR0vNtKVQVRpVshnU0z223TsDckrHfz7QQuBg4zyaZLqUAO61barMS9DbqZL22UCn0v5oe2f5V3nkCbfo8AALaeCCzLMETnyJ2fcmpJ0-DTkXmyiY_S05-2K_5TObRMbfmlGokg8xDDrtOyq9A5uZtJVqNusoQavQDFGv4-cmJofcbVHqOdDbqTBiMUvfuflu-wtm4pKRBs4bLXzTY3sE9OUPZBo9ZbEIoGLW7KQOmHEoMobDzTBz5MgiiVSd1YJOuxZtB_aHeR21sEy1BN6TkaUMoyidES9SOS_386Sejn4C4vRgAkMmGxaTD5WvT_Cem-H46IZENvLbzIjdoUblA2HfnfQ3Eg9gOblZlE3_MUql6We-giWM6J6B2y5aCyQ=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-04-14T19:45:00.000Z", "utc_arrival": "2023-04-14T17:45:00.000Z", "local_departure": "2023-04-14T16:15:00.000Z", "utc_departure": "2023-04-14T14:15:00.000Z"}, {"id": "0b770a224c43000004103d82_0|0a220b774c47000069bc4867_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 729.643099, "distance": 1975.87, "duration": {"departure": 11700, "return": 11700, "total": 23400}, "price": 220663.5746, "conversion": {"EUR": 577.643479, "HUF": 220663.5746}, "fare": {"adults": 110331.79, "children": 110331.79, "infants": 110331.79}, "bags_price": {"1": 97.118, "2": 204.036}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 158, "hold_height": 52, "hold_length": 78, "hold_weight": 20, "hold_width": 28, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 3, "personal_item_width": 15}, "availability": {"seats": 2}, "airlines": ["W6", "IB"], "route": [{"id": "0b770a224c43000004103d82_0", "combination_id": "0b770a224c43000004103d82", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "IB", "flight_no": 3279, "operating_carrier": "IB", "operating_flight_no": "3279", "fare_basis": "ADNNAOB4", "fare_category": "M", "fare_classes": "A", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-15T18:50:00.000Z", "utc_arrival": "2023-06-15T16:50:00.000Z", "local_departure": "2023-06-15T15:35:00.000Z", "utc_departure": "2023-06-15T13:35:00.000Z"}, {"id": "0a220b774c47000069bc4867_0", "combination_id": "0a220b774c47000069bc4867", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-19T23:45:00.000Z", "utc_arrival": "2023-06-19T21:45:00.000Z", "local_departure": "2023-06-19T20:30:00.000Z", "utc_departure": "2023-06-19T18:30:00.000Z"}], "booking_token": "EtEjfIgQKaw7YbecT8eAErV0znto9d8psMd1d5yCfHx62Ot9e5hoefYUqwyI7VtzmHQ2cphBfGBSm5xd-7YB_OtG9M-KgYKdmOr0RfzGXnJlPjFPNx7hI7QFA7EWUYmPnrH3YWnJ3i_ht7IF_rHaQDXq3q8ur4u5ba_RpofldAXgzX24vII2DVLkw9JZgJA1joq2s9l4wOvZLBUjlq0atlXZn37nUfqYvF8rFhjzzbZMCQZXruOM4Y3JLfBHenR2__0oO7fH78yslSYjLG6B_abWy53pegHfRG0rRojZqZSLKtC0kqCitTuQ72-08mFdvnM3QyYdRRtWzMa3eBzDXoDMGTohKMlSVQhJ73dXC9ZAk6en7RuE-leanpOw-OENBnH4STLF0HmtxjocP6hlII4y-o1xq-g6zSpkAMHllMb8hdcnRceRiE1r7grzA5Y5M2WG8hcXutFwtOQzLS-j5aUWw4Q6jqXTlrChgdWsexsdySCk2glA-So8NAGNJjtZYnCVjlOwrIM5c58xTR_ci-vsmKJt6EeHovODQKcppobGdflRuPYOcnE1RutWIwHD9WRr8WDXG1fwfiyWUsG5sNKN6GwqTK74wRRLezjFNqThApqwx7rElfVe12PtPsp3qqZT-euDokIl27MRyB3fwLKpDixuRpzHXUfScuH4DYU1bCouk1o8sWmlKbfVSL8ejKJpcC1RcyneScevL1Ds1d7-Of4x8oVir9Oal24cU04CulHGUvGvqDhGvNhNU721bwBBdKoGZlzudcPNwmPpEQcPOhc796Mvsgxn4do3bhcj0zf-oyIdsh8Zzo-f9zZVC", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c43000004103d82_0%7C0a220b774c47000069bc4867_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EtEjfIgQKaw7YbecT8eAErV0znto9d8psMd1d5yCfHx62Ot9e5hoefYUqwyI7VtzmHQ2cphBfGBSm5xd-7YB_OtG9M-KgYKdmOr0RfzGXnJlPjFPNx7hI7QFA7EWUYmPnrH3YWnJ3i_ht7IF_rHaQDXq3q8ur4u5ba_RpofldAXgzX24vII2DVLkw9JZgJA1joq2s9l4wOvZLBUjlq0atlXZn37nUfqYvF8rFhjzzbZMCQZXruOM4Y3JLfBHenR2__0oO7fH78yslSYjLG6B_abWy53pegHfRG0rRojZqZSLKtC0kqCitTuQ72-08mFdvnM3QyYdRRtWzMa3eBzDXoDMGTohKMlSVQhJ73dXC9ZAk6en7RuE-leanpOw-OENBnH4STLF0HmtxjocP6hlII4y-o1xq-g6zSpkAMHllMb8hdcnRceRiE1r7grzA5Y5M2WG8hcXutFwtOQzLS-j5aUWw4Q6jqXTlrChgdWsexsdySCk2glA-So8NAGNJjtZYnCVjlOwrIM5c58xTR_ci-vsmKJt6EeHovODQKcppobGdflRuPYOcnE1RutWIwHD9WRr8WDXG1fwfiyWUsG5sNKN6GwqTK74wRRLezjFNqThApqwx7rElfVe12PtPsp3qqZT-euDokIl27MRyB3fwLKpDixuRpzHXUfScuH4DYU1bCouk1o8sWmlKbfVSL8ejKJpcC1RcyneScevL1Ds1d7-Of4x8oVir9Oal24cU04CulHGUvGvqDhGvNhNU721bwBBdKoGZlzudcPNwmPpEQcPOhc796Mvsgxn4do3bhcj0zf-oyIdsh8Zzo-f9zZVC", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-15T18:50:00.000Z", "utc_arrival": "2023-06-15T16:50:00.000Z", "local_departure": "2023-06-15T15:35:00.000Z", "utc_departure": "2023-06-15T13:35:00.000Z"}, {"id": "0b770a224c280000d84fb6b2_0|0a220b774c2c000089e7df3d_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 732.348117, "distance": 1975.87, "duration": {"departure": 12600, "return": 11400, "total": 24000}, "price": 220678.2276, "conversion": {"EUR": 577.681837, "HUF": 220678.2276}, "fare": {"adults": 110339.11, "children": 110339.11, "infants": 110339.11}, "bags_price": {"1": 92.204, "2": 184.422}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 3}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224c280000d84fb6b2_0", "combination_id": "0b770a224c280000d84fb6b2", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-19T19:45:00.000Z", "utc_arrival": "2023-05-19T17:45:00.000Z", "local_departure": "2023-05-19T16:15:00.000Z", "utc_departure": "2023-05-19T14:15:00.000Z"}, {"id": "0a220b774c2c000089e7df3d_0", "combination_id": "0a220b774c2c000089e7df3d", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-23T14:05:00.000Z", "utc_arrival": "2023-05-23T12:05:00.000Z", "local_departure": "2023-05-23T10:55:00.000Z", "utc_departure": "2023-05-23T08:55:00.000Z"}], "booking_token": "EExgHhsqhvEZJGP1SsF7iXianMhBYBpjGjivSAGU-vj-C7aodGXm687gPPNUTWKwFM0T1Wqgy0mPFyE_c_eEgv548SVq7bzqKsZ7Py7S4Fg31TlKEMROfYn2nLLg8xHBQ_P-PYpnH6Xrh5-Fg7jQs8u0vTuD24RMHy6dNA70G9As_pXQxUyLnBSUjGhcrFPjSgSnV7nwlWIgg44C4GTv4NSXqaMxEFHUwGBd6bLjvv4E3SEGXg7q16PqjGBCob5bkiVoofjet1YRpEwQL-CjWwFwvJwNEYEUgFdf9XyR-CRT_H6PV24LSLUfc7l1sd66-9FNxvJCqHHyuKdbr7UqzDjx5nQAlqanq382Zt5acHgXUAoazpV2FXeGFuVspid5ZzlgbTRmfsXVpIFeUNQLZLOje3VjcRmHSPspe-qiFbPvQNYBseOjuYaHyswZUu380ZRW91t4BmCAY0TNNuAa16RsgM_xeMfMyDGG5Zx06ZU0qtJfEDtUKT_pndQycdLQilcU0IXASDBCbPGNtLIHek54_L82s4LDXUvh_tbhet0ZTLBf36RStdQOcmn4ZPnCD0DALkbhqiDOnMMFw4m7xY2TCgsRGEavLUJiv0-hW9DWYtwLj8fy7_u9ZtgGIXjA54ts6WA04uxE6zWVbKtw4JOaNQmDU9i466GloaMgFJaYb8rPvc_Lf6mx8eXf62GvAiJ-QYgrkegZ3Ljt8yKPiXq2kx1DfwAccoHwNItAQBD6M066kQ9Tkx6wh0yZennPptNw8ZVo0yjbV1HuTh3zUGA==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c280000d84fb6b2_0%7C0a220b774c2c000089e7df3d_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EExgHhsqhvEZJGP1SsF7iXianMhBYBpjGjivSAGU-vj-C7aodGXm687gPPNUTWKwFM0T1Wqgy0mPFyE_c_eEgv548SVq7bzqKsZ7Py7S4Fg31TlKEMROfYn2nLLg8xHBQ_P-PYpnH6Xrh5-Fg7jQs8u0vTuD24RMHy6dNA70G9As_pXQxUyLnBSUjGhcrFPjSgSnV7nwlWIgg44C4GTv4NSXqaMxEFHUwGBd6bLjvv4E3SEGXg7q16PqjGBCob5bkiVoofjet1YRpEwQL-CjWwFwvJwNEYEUgFdf9XyR-CRT_H6PV24LSLUfc7l1sd66-9FNxvJCqHHyuKdbr7UqzDjx5nQAlqanq382Zt5acHgXUAoazpV2FXeGFuVspid5ZzlgbTRmfsXVpIFeUNQLZLOje3VjcRmHSPspe-qiFbPvQNYBseOjuYaHyswZUu380ZRW91t4BmCAY0TNNuAa16RsgM_xeMfMyDGG5Zx06ZU0qtJfEDtUKT_pndQycdLQilcU0IXASDBCbPGNtLIHek54_L82s4LDXUvh_tbhet0ZTLBf36RStdQOcmn4ZPnCD0DALkbhqiDOnMMFw4m7xY2TCgsRGEavLUJiv0-hW9DWYtwLj8fy7_u9ZtgGIXjA54ts6WA04uxE6zWVbKtw4JOaNQmDU9i466GloaMgFJaYb8rPvc_Lf6mx8eXf62GvAiJ-QYgrkegZ3Ljt8yKPiXq2kx1DfwAccoHwNItAQBD6M066kQ9Tkx6wh0yZennPptNw8ZVo0yjbV1HuTh3zUGA==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-19T19:45:00.000Z", "utc_arrival": "2023-05-19T17:45:00.000Z", "local_departure": "2023-05-19T16:15:00.000Z", "utc_departure": "2023-05-19T14:15:00.000Z"}, {"id": "0b770a224c350000fd39ce98_0|0a220b774c390000ac91a717_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 733.612715, "distance": 1975.87, "duration": {"departure": 12600, "return": 11400, "total": 24000}, "price": 221161.3123, "conversion": {"EUR": 578.946435, "HUF": 221161.3123}, "fare": {"adults": 110580.66, "children": 110580.66, "infants": 110580.66}, "bags_price": {"1": 93.744, "2": 187.488}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 2}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224c350000fd39ce98_0", "combination_id": "0b770a224c350000fd39ce98", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "HREG", "fare_category": "M", "fare_classes": "H", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-01T21:15:00.000Z", "utc_arrival": "2023-06-01T19:15:00.000Z", "local_departure": "2023-06-01T17:45:00.000Z", "utc_departure": "2023-06-01T15:45:00.000Z"}, {"id": "0a220b774c390000ac91a717_0", "combination_id": "0a220b774c390000ac91a717", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-05T10:15:00.000Z", "utc_arrival": "2023-06-05T08:15:00.000Z", "local_departure": "2023-06-05T07:05:00.000Z", "utc_departure": "2023-06-05T05:05:00.000Z"}], "booking_token": "EsNx2UHarYM8mKIUD4RGV2Jdn0iJSeJP8b--9WcB8_AlpGlZ0p1dC3FRj6GMMFOT-tCCm1MtALgMCkt5Hvdj2q_aEFqujgnHCEHCQ8myLzQIs3W8IqDHKpBm6Ie_-LVW-GQGIlcwcuI8tiLzZhSmf0aJ5fXH-i_807ensNRN6kRLc2nBvRcdJ8sssyi0WTnSycPH9CQ5ed-IJ5k9ZmEKDgvLmozN7qemkp2zICtNPyuWPGhOmScSBpLQ04owzlzQr_Ettpozpn_HsAFdMzRJwDWlnVZodxMMNWswfa0cYVroMoXXF98TP6awcNp4Im2I_OSi2aPXzF63Qn0NdsecSFTL8LOlQXVpcYK6EVnybFzZLj28-nJ8Rlwa9GiS6NzFPNwBVWTwWFYectXcYgO5hcHLnY9c_gp2A8GOP1MkzcV_QJLahIOp8uQSz4sm2jSag4fopOzDnJxPKq_XVeXHPqi1lKXreVBBjr8JpoktJ9EQKICzWpspaSaeKvv-PctL8eooGEEGjJtd0kLPOKrhF2_qtGzy7frKHY87ePTB_yK9b-icQoaHSrTu_lzo4AkiI3xYzcIdlxCjKDcSfoi2ckiCwhjQ3_nxtNo-X2urAdC4wCCJrRh6aJtmEOOyMlSDRVLo3oM35TpmDRj1Xr9HzteNafRq3i4pPzPIi8vx9AOEWVsUnV60889TELl1ycBUVHllLD_6IlRW1Og9bJtmOcj3MNZpMJC_wlCZv4vk-vispP5V0HcjAMgNXE0NJR4j_o34CDIcpavnA6HFQoj_DPg5XpHG3E7S5sRuFX8hjsmM=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c350000fd39ce98_0%7C0a220b774c390000ac91a717_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EsNx2UHarYM8mKIUD4RGV2Jdn0iJSeJP8b--9WcB8_AlpGlZ0p1dC3FRj6GMMFOT-tCCm1MtALgMCkt5Hvdj2q_aEFqujgnHCEHCQ8myLzQIs3W8IqDHKpBm6Ie_-LVW-GQGIlcwcuI8tiLzZhSmf0aJ5fXH-i_807ensNRN6kRLc2nBvRcdJ8sssyi0WTnSycPH9CQ5ed-IJ5k9ZmEKDgvLmozN7qemkp2zICtNPyuWPGhOmScSBpLQ04owzlzQr_Ettpozpn_HsAFdMzRJwDWlnVZodxMMNWswfa0cYVroMoXXF98TP6awcNp4Im2I_OSi2aPXzF63Qn0NdsecSFTL8LOlQXVpcYK6EVnybFzZLj28-nJ8Rlwa9GiS6NzFPNwBVWTwWFYectXcYgO5hcHLnY9c_gp2A8GOP1MkzcV_QJLahIOp8uQSz4sm2jSag4fopOzDnJxPKq_XVeXHPqi1lKXreVBBjr8JpoktJ9EQKICzWpspaSaeKvv-PctL8eooGEEGjJtd0kLPOKrhF2_qtGzy7frKHY87ePTB_yK9b-icQoaHSrTu_lzo4AkiI3xYzcIdlxCjKDcSfoi2ckiCwhjQ3_nxtNo-X2urAdC4wCCJrRh6aJtmEOOyMlSDRVLo3oM35TpmDRj1Xr9HzteNafRq3i4pPzPIi8vx9AOEWVsUnV60889TELl1ycBUVHllLD_6IlRW1Og9bJtmOcj3MNZpMJC_wlCZv4vk-vispP5V0HcjAMgNXE0NJR4j_o34CDIcpavnA6HFQoj_DPg5XpHG3E7S5sRuFX8hjsmM=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-01T21:15:00.000Z", "utc_arrival": "2023-06-01T19:15:00.000Z", "local_departure": "2023-06-01T17:45:00.000Z", "utc_departure": "2023-06-01T15:45:00.000Z"}, {"id": "0b770a224c040000025fb1e5_0|0a220b774c070000c2364b8c_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 736.390253, "distance": 1975.87, "duration": {"departure": 12600, "return": 11700, "total": 24300}, "price": 221713.0092, "conversion": {"EUR": 580.390643, "HUF": 221713.0092}, "fare": {"adults": 110856.5, "children": 110856.5, "infants": 110856.5}, "bags_price": {"1": 129.36, "2": 258.72}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 439, "hold_height": 149, "hold_length": 171, "hold_weight": 20, "hold_width": 119, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 3}, "airlines": ["W6"], "route": [{"id": "0b770a224c040000025fb1e5_0", "combination_id": "0b770a224c040000025fb1e5", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-13T21:15:00.000Z", "utc_arrival": "2023-04-13T19:15:00.000Z", "local_departure": "2023-04-13T17:45:00.000Z", "utc_departure": "2023-04-13T15:45:00.000Z"}, {"id": "0a220b774c070000c2364b8c_0", "combination_id": "0a220b774c070000c2364b8c", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "LREG", "fare_category": "M", "fare_classes": "L", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-16T21:05:00.000Z", "utc_arrival": "2023-04-16T19:05:00.000Z", "local_departure": "2023-04-16T17:50:00.000Z", "utc_departure": "2023-04-16T15:50:00.000Z"}], "booking_token": "ExRqKLuMvGED5JeCQYeaIhX5o6sumgVRky6zerHI6mkR0rUYt2-vUWm5wTUEogyoIrsYJmCGS55imn3b4-FBz29Zcn1Q6A_HMXk6bby9UT7NOYzbi0vBorByiPPGbwfOjQze08-xTDbe3liBk_c_C4L37JBJYtkHtMJ0bsES5jZ3jEuI926MKLd-amq6eMFhJskQ1p88akEjZspAah-GrxIKkLFlC0100tLxgkGaFGJQLzjg2DxbiJ330jdafcaTYtx29rElPayYCx24j4MIDHFu5Op29aLj2oGqsSAOt7ftwSzg5bABciU7mYEMtfzxsv268tg_g4SV3dDY4CJQiH0laL-sO3qKV3E9GFShIJln4ICPkbaNjC-K6mNyKKeNKQzPrDpY21fsTDLugSdN-lfDMRuA1IHqYLtUIl6F3RXP068V_RchmUvu-6fEWv09HehUckiRgwDjHTm663zF28GnkgIbpUVrrbXDRSMF3KTRsmS4ubK5q7muY_cxey9bnDcvLAZed0bDaYW69hzx1fpgl57uovrxm43Kx2oLKQARbJOZpA6qCgzec5UTXaS0V0HTXYi41VoRGkhDww7N968lMVJBFRt1hCaVv_VSfLwOLwV7-3cuYC9M_hfIwA-Ut8nYwN1lQTN6n49dYULRIw1SOS3LbfSmm49XuZrlPBupt6KvdYM46sA34VjKGnOiwaaJ1bbgOD2uhbPGdQ0Ra9T69VNmJSDG9lFg4ycWSw6I0rTjYoMnE8HkWvj8FJWsOv03X0djsQnQaVZVKxC-dVOfMj6Bxvzh8as6hk1Q9-08=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c040000025fb1e5_0%7C0a220b774c070000c2364b8c_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=ExRqKLuMvGED5JeCQYeaIhX5o6sumgVRky6zerHI6mkR0rUYt2-vUWm5wTUEogyoIrsYJmCGS55imn3b4-FBz29Zcn1Q6A_HMXk6bby9UT7NOYzbi0vBorByiPPGbwfOjQze08-xTDbe3liBk_c_C4L37JBJYtkHtMJ0bsES5jZ3jEuI926MKLd-amq6eMFhJskQ1p88akEjZspAah-GrxIKkLFlC0100tLxgkGaFGJQLzjg2DxbiJ330jdafcaTYtx29rElPayYCx24j4MIDHFu5Op29aLj2oGqsSAOt7ftwSzg5bABciU7mYEMtfzxsv268tg_g4SV3dDY4CJQiH0laL-sO3qKV3E9GFShIJln4ICPkbaNjC-K6mNyKKeNKQzPrDpY21fsTDLugSdN-lfDMRuA1IHqYLtUIl6F3RXP068V_RchmUvu-6fEWv09HehUckiRgwDjHTm663zF28GnkgIbpUVrrbXDRSMF3KTRsmS4ubK5q7muY_cxey9bnDcvLAZed0bDaYW69hzx1fpgl57uovrxm43Kx2oLKQARbJOZpA6qCgzec5UTXaS0V0HTXYi41VoRGkhDww7N968lMVJBFRt1hCaVv_VSfLwOLwV7-3cuYC9M_hfIwA-Ut8nYwN1lQTN6n49dYULRIw1SOS3LbfSmm49XuZrlPBupt6KvdYM46sA34VjKGnOiwaaJ1bbgOD2uhbPGdQ0Ra9T69VNmJSDG9lFg4ycWSw6I0rTjYoMnE8HkWvj8FJWsOv03X0djsQnQaVZVKxC-dVOfMj6Bxvzh8as6hk1Q9-08=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-04-13T21:15:00.000Z", "utc_arrival": "2023-04-13T19:15:00.000Z", "local_departure": "2023-04-13T17:45:00.000Z", "utc_departure": "2023-04-13T15:45:00.000Z"}, {"id": "0b770a224c3d000092cf2d05_0|0a220b774c4100004abd18f4_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 732.836624, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 221883.522, "conversion": {"EUR": 580.837004, "HUF": 221883.522}, "fare": {"adults": 110941.76, "children": 110941.76, "infants": 110941.76}, "bags_price": {"1": 76.762, "2": 163.338}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 158, "hold_height": 52, "hold_length": 78, "hold_weight": 20, "hold_width": 28, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 3, "personal_item_width": 15}, "availability": {"seats": 6}, "airlines": ["FR", "IB"], "route": [{"id": "0b770a224c3d000092cf2d05_0", "combination_id": "0b770a224c3d000092cf2d05", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-09T21:45:00.000Z", "utc_arrival": "2023-06-09T19:45:00.000Z", "local_departure": "2023-06-09T18:25:00.000Z", "utc_departure": "2023-06-09T16:25:00.000Z"}, {"id": "0a220b774c4100004abd18f4_0", "combination_id": "0a220b774c4100004abd18f4", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "IB", "flight_no": 3278, "operating_carrier": "IB", "operating_flight_no": "3278", "fare_basis": "NWNNAOB4", "fare_category": "M", "fare_classes": "N", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-13T14:55:00.000Z", "utc_arrival": "2023-06-13T12:55:00.000Z", "local_departure": "2023-06-13T11:45:00.000Z", "utc_departure": "2023-06-13T09:45:00.000Z"}], "booking_token": "EQ4gLSYmCWIJ9KXkafOgTY0zrA17b443D5UlmN2_Ji6K7ph-gayzIeXKXk9zbJDhek6KYYwb3UALp0dodTkhKEm58aqqMAF2FdGDuMJHe2YGAg-w8XwfZghMxRXGzBH4rO04n9vDFWOmLa5oVxU2pUF2fDMIDxFsRENcG1RvzTF4qSEls6Yk_tZgNH9tQdmqlKj1g2IazIDyXN4pNIF_HD8ccPNbBanrNphN8Bn6oTUw3B8VJuya13OY3ZZHPZv_w_MmGGKq7iidBNsWEwBB6aMeB3fVUFdCQIWW_d58h7pDDc2vy_w6sdKK3RFFKvrV5pDzoyWEIWeC4iSO4zv5xpn-cZEcQ_jMER4OyS2qgC_5R8bBBl-EFDRXmFK2W6Kp5HUdYO0iK00P1dK-vHH52dJZMMMCVFI6PoAEclBbB541OUtnoMEGEPbgH_B31K_HX2RXiXZXLUavI-L_z3un_nLpy37YoJ-qdjgiBA4obfowYKJxwzrzvtevXTuaOgxL8NkwpjYaI-MNX0j5u1oxxHsx6wEioVMBsQYpVYKVmJPOMIODv7VCwGLpkca3ANYiLl9sRoqbQ8J6KEvikFnokrD8-b235EbWNvDFlZe-K9zcCRT2USGCIwcP66F06yKnE57LvT5_xThvBdX-uAYCn-MFbzQGk_nNH0QdcgAeL67E_XSauS7LvTmhHbIgTKNc_H1QfghN7fYvYlCJvCMgtyZFlEYTwLo-IjDytDgLaqDk=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c3d000092cf2d05_0%7C0a220b774c4100004abd18f4_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EQ4gLSYmCWIJ9KXkafOgTY0zrA17b443D5UlmN2_Ji6K7ph-gayzIeXKXk9zbJDhek6KYYwb3UALp0dodTkhKEm58aqqMAF2FdGDuMJHe2YGAg-w8XwfZghMxRXGzBH4rO04n9vDFWOmLa5oVxU2pUF2fDMIDxFsRENcG1RvzTF4qSEls6Yk_tZgNH9tQdmqlKj1g2IazIDyXN4pNIF_HD8ccPNbBanrNphN8Bn6oTUw3B8VJuya13OY3ZZHPZv_w_MmGGKq7iidBNsWEwBB6aMeB3fVUFdCQIWW_d58h7pDDc2vy_w6sdKK3RFFKvrV5pDzoyWEIWeC4iSO4zv5xpn-cZEcQ_jMER4OyS2qgC_5R8bBBl-EFDRXmFK2W6Kp5HUdYO0iK00P1dK-vHH52dJZMMMCVFI6PoAEclBbB541OUtnoMEGEPbgH_B31K_HX2RXiXZXLUavI-L_z3un_nLpy37YoJ-qdjgiBA4obfowYKJxwzrzvtevXTuaOgxL8NkwpjYaI-MNX0j5u1oxxHsx6wEioVMBsQYpVYKVmJPOMIODv7VCwGLpkca3ANYiLl9sRoqbQ8J6KEvikFnokrD8-b235EbWNvDFlZe-K9zcCRT2USGCIwcP66F06yKnE57LvT5_xThvBdX-uAYCn-MFbzQGk_nNH0QdcgAeL67E_XSauS7LvTmhHbIgTKNc_H1QfghN7fYvYlCJvCMgtyZFlEYTwLo-IjDytDgLaqDk=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-09T21:45:00.000Z", "utc_arrival": "2023-06-09T19:45:00.000Z", "local_departure": "2023-06-09T18:25:00.000Z", "utc_departure": "2023-06-09T16:25:00.000Z"}, {"id": "0b770a224c0b000076bbcc9c_0|0a220b774c0e0000c501735e_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 733.301014, "distance": 1975.87, "duration": {"departure": 11700, "return": 11700, "total": 23400}, "price": 222060.922, "conversion": {"EUR": 581.301394, "HUF": 222060.922}, "fare": {"adults": 111030.46, "children": 111030.46, "infants": 111030.46}, "bags_price": {"1": 67.9, "2": 145.6}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 158, "hold_height": 52, "hold_length": 78, "hold_weight": 20, "hold_width": 28, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 3, "personal_item_width": 15}, "availability": {"seats": 3}, "airlines": ["W6", "IB"], "route": [{"id": "0b770a224c0b000076bbcc9c_0", "combination_id": "0b770a224c0b000076bbcc9c", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "IB", "flight_no": 3279, "operating_carrier": "IB", "operating_flight_no": "3279", "fare_basis": "QDNNAOB4", "fare_category": "M", "fare_classes": "Q", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-20T18:50:00.000Z", "utc_arrival": "2023-04-20T16:50:00.000Z", "local_departure": "2023-04-20T15:35:00.000Z", "utc_departure": "2023-04-20T13:35:00.000Z"}, {"id": "0a220b774c0e0000c501735e_0", "combination_id": "0a220b774c0e0000c501735e", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "JREG", "fare_category": "M", "fare_classes": "J", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-23T21:05:00.000Z", "utc_arrival": "2023-04-23T19:05:00.000Z", "local_departure": "2023-04-23T17:50:00.000Z", "utc_departure": "2023-04-23T15:50:00.000Z"}], "booking_token": "ECxx6_htwO9aONmwg3iUDLE8G-5-IZtOkP8IClZQ1UGqWSMY3D-vnAJoFjWzlNsVrm7jvCuFrHD42B3CsQ9fp-d5SLbLP-6ViUdGptqz4qYqB74NkaKZpjVc6uAwaYwWBUJnzeXL7ClG7aGoy8QpG3MUmTHG6puh8U6I2nXoNRo4crbWkzA9wOl4sox4i4DdWqg7dhVA8rPBcipa1l_fBdsbUWcppZYSJkdYikvLq4gfZzkknRWTUHcAJcpFMZHmxtr76_jdOVWk_7xMAnOayPIbs0TUjZ1sHbAkTu2jpE4bPsxAQzTggsm69whZ-i15C8qLnLKJ4fKre-FIW5wWLslrfwTbN1CPDSqL0eE53x5H6xo45tgY2MYQLawMMVoAYlm7aw0E2eT3ygdulQFTF-kcMfI9IYlL3QFG9c95fgQMMwiRdl7yOb2SZZjRjalNFd5KQRnazroIY--OxlpgLaddJkjp1I559tJN5LwJUnd4DptrlbK6-8p4NnbR-0u-KWkumco0VbLSO039BLD3mbdDRjH6YAELqjrWR4bApRJoKY-xITCw6aLWpGM-L7S-iEabFVemHZazcwVJSwoolPMbdxtcW3qDv97J5wLmooaGK9EOsml2Z8hoD-qE4M_1iLf167DIZwnQTH-o58LNUlctQdEmvx34fzJbUi0W6n25TzgiNLy83B193lqrbm4B70GyfpZ_dRQ3GhSkMnb2HC8nKMbq3h-ienpjD1jcA8ObPZEiti3muwa7n50kK5p4McTupaOanYZsLvTRKu24QWO6TA9XSoOiYumA7HTdBQnpvzJODCxBymZMg_UUvhjK1", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c0b000076bbcc9c_0%7C0a220b774c0e0000c501735e_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=ECxx6_htwO9aONmwg3iUDLE8G-5-IZtOkP8IClZQ1UGqWSMY3D-vnAJoFjWzlNsVrm7jvCuFrHD42B3CsQ9fp-d5SLbLP-6ViUdGptqz4qYqB74NkaKZpjVc6uAwaYwWBUJnzeXL7ClG7aGoy8QpG3MUmTHG6puh8U6I2nXoNRo4crbWkzA9wOl4sox4i4DdWqg7dhVA8rPBcipa1l_fBdsbUWcppZYSJkdYikvLq4gfZzkknRWTUHcAJcpFMZHmxtr76_jdOVWk_7xMAnOayPIbs0TUjZ1sHbAkTu2jpE4bPsxAQzTggsm69whZ-i15C8qLnLKJ4fKre-FIW5wWLslrfwTbN1CPDSqL0eE53x5H6xo45tgY2MYQLawMMVoAYlm7aw0E2eT3ygdulQFTF-kcMfI9IYlL3QFG9c95fgQMMwiRdl7yOb2SZZjRjalNFd5KQRnazroIY--OxlpgLaddJkjp1I559tJN5LwJUnd4DptrlbK6-8p4NnbR-0u-KWkumco0VbLSO039BLD3mbdDRjH6YAELqjrWR4bApRJoKY-xITCw6aLWpGM-L7S-iEabFVemHZazcwVJSwoolPMbdxtcW3qDv97J5wLmooaGK9EOsml2Z8hoD-qE4M_1iLf167DIZwnQTH-o58LNUlctQdEmvx34fzJbUi0W6n25TzgiNLy83B193lqrbm4B70GyfpZ_dRQ3GhSkMnb2HC8nKMbq3h-ienpjD1jcA8ObPZEiti3muwa7n50kK5p4McTupaOanYZsLvTRKu24QWO6TA9XSoOiYumA7HTdBQnpvzJODCxBymZMg_UUvhjK1", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-04-20T18:50:00.000Z", "utc_arrival": "2023-04-20T16:50:00.000Z", "local_departure": "2023-04-20T15:35:00.000Z", "utc_departure": "2023-04-20T13:35:00.000Z"}, {"id": "0b770a224c4b00004d10476b_0|0a220b774c4e0000de14d559_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 739.678513, "distance": 1975.87, "duration": {"departure": 12600, "return": 11700, "total": 24300}, "price": 222969.1459, "conversion": {"EUR": 583.678903, "HUF": 222969.1459}, "fare": {"adults": 111484.57, "children": 115043.2, "infants": 115043.2}, "bags_price": {"1": 123.242, "2": 246.47}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 439, "hold_height": 149, "hold_length": 171, "hold_weight": 20, "hold_width": 119, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 5}, "airlines": ["W6"], "route": [{"id": "0b770a224c4b00004d10476b_0", "combination_id": "0b770a224c4b00004d10476b", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IJREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-23T19:45:00.000Z", "utc_arrival": "2023-06-23T17:45:00.000Z", "local_departure": "2023-06-23T16:15:00.000Z", "utc_departure": "2023-06-23T14:15:00.000Z"}, {"id": "0a220b774c4e0000de14d559_0", "combination_id": "0a220b774c4e0000de14d559", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IJREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-26T23:45:00.000Z", "utc_arrival": "2023-06-26T21:45:00.000Z", "local_departure": "2023-06-26T20:30:00.000Z", "utc_departure": "2023-06-26T18:30:00.000Z"}], "booking_token": "ECmHg8uQA-rrOWxjUHWYs-hmLvf6fHSBONYcYxVhflagU6UPMYpKOrkj6Za00xi2JhhU_UZBob23cfJrjbsl0oPIe-DKMbYWRZ3_OfXB0rsOC1OeAAszaIW4LbfS6CFkne3KLEmdTgtRLCd05AWafeeyj3amZshkg5XjmmwuLSGq0yIjru7GdguLRx7DbHbH2vnWgHSSduo4qH9yT4JhDeBNJSr5wU5ji4-vYwU4cE5-mjUFXvMtMsJ8diaT0DkNUYR0as531cnDj2U3FNhy1Jm_G6cvGTjjK5Fztcl4UaWlJXN65g6ngCfZBYkX2xbwXl_nhfSDMTl7eBU7S-slSISxKZp1ohvVOVtvcTyf4ft3DgLinDWzEwILjxGnRhzRz55pCqu4FZv0pEmLUoZZedJkkTPc3OBQiRN8zetzkFiH5iIrhCKA7XqfNmklZHJUgsQkQ-bWFetlPVyueu7myx61F0saBlRlUWV1eHliq-1IdAiTOTslSJfe4uq03NcEd-1faDWyfbEd3dfHk1HBbdIO9Tp7Cr1rt87u_z6ma1Uytw9nCjHmEHz4LDiyU3qRUb7MXXpoS4AzEPxhP5YOxNfFMA36KBWnJsOpL4WCMYksb7E2mmhSjJvu3rgoaIL_S7lSV1678CxrjPhvKrMZk5QbhBykvTF8Ge7Q6M16cx4wu06FxCY-Bkn9w2Sp9Rbo9C3XMNPtVcgwcV2f6KG9Kh3UDe53ujkE3Y3SK0tCR2DOrKtYLomX8vz8uagYxP7vTwIdhKHpOaKEPQHxuPQRKpbmFtPG9zjtWHbE2yswFna0=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c4b00004d10476b_0%7C0a220b774c4e0000de14d559_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=ECmHg8uQA-rrOWxjUHWYs-hmLvf6fHSBONYcYxVhflagU6UPMYpKOrkj6Za00xi2JhhU_UZBob23cfJrjbsl0oPIe-DKMbYWRZ3_OfXB0rsOC1OeAAszaIW4LbfS6CFkne3KLEmdTgtRLCd05AWafeeyj3amZshkg5XjmmwuLSGq0yIjru7GdguLRx7DbHbH2vnWgHSSduo4qH9yT4JhDeBNJSr5wU5ji4-vYwU4cE5-mjUFXvMtMsJ8diaT0DkNUYR0as531cnDj2U3FNhy1Jm_G6cvGTjjK5Fztcl4UaWlJXN65g6ngCfZBYkX2xbwXl_nhfSDMTl7eBU7S-slSISxKZp1ohvVOVtvcTyf4ft3DgLinDWzEwILjxGnRhzRz55pCqu4FZv0pEmLUoZZedJkkTPc3OBQiRN8zetzkFiH5iIrhCKA7XqfNmklZHJUgsQkQ-bWFetlPVyueu7myx61F0saBlRlUWV1eHliq-1IdAiTOTslSJfe4uq03NcEd-1faDWyfbEd3dfHk1HBbdIO9Tp7Cr1rt87u_z6ma1Uytw9nCjHmEHz4LDiyU3qRUb7MXXpoS4AzEPxhP5YOxNfFMA36KBWnJsOpL4WCMYksb7E2mmhSjJvu3rgoaIL_S7lSV1678CxrjPhvKrMZk5QbhBykvTF8Ge7Q6M16cx4wu06FxCY-Bkn9w2Sp9Rbo9C3XMNPtVcgwcV2f6KG9Kh3UDe53ujkE3Y3SK0tCR2DOrKtYLomX8vz8uagYxP7vTwIdhKHpOaKEPQHxuPQRKpbmFtPG9zjtWHbE2yswFna0=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-23T19:45:00.000Z", "utc_arrival": "2023-06-23T17:45:00.000Z", "local_departure": "2023-06-23T16:15:00.000Z", "utc_departure": "2023-06-23T14:15:00.000Z"}, {"id": "0b770a224c1a0000fc0feb0f_0|0a220b774c1d00006b072ab9_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 738.570854, "distance": 1975.87, "duration": {"departure": 12600, "return": 11400, "total": 24000}, "price": 223055.3537, "conversion": {"EUR": 583.904574, "HUF": 223055.3537}, "fare": {"adults": 111527.68, "children": 116648.19, "infants": 116648.19}, "bags_price": {"1": 88.508, "2": 177.016}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 6}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224c1a0000fc0feb0f_0", "combination_id": "0b770a224c1a0000fc0feb0f", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "JREG", "fare_category": "M", "fare_classes": "J", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-05T19:45:00.000Z", "utc_arrival": "2023-05-05T17:45:00.000Z", "local_departure": "2023-05-05T16:15:00.000Z", "utc_departure": "2023-05-05T14:15:00.000Z"}, {"id": "0a220b774c1d00006b072ab9_0", "combination_id": "0a220b774c1d00006b072ab9", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-08T10:15:00.000Z", "utc_arrival": "2023-05-08T08:15:00.000Z", "local_departure": "2023-05-08T07:05:00.000Z", "utc_departure": "2023-05-08T05:05:00.000Z"}], "booking_token": "EVEjOvsoJKF7xr3cLwZGQa3EyfMVei8Qnv6vhuEP-4WqOysOddDn0u_oe98H5sAfcUOHoDoi_i5G7YuDu-61jEYqq_Xc3Zyxbw6MVrGmZ5ve8HDCCop39xztA6l2eU9PeWOXiBtlzifJ0IJQkA90Nx-sjAynQUxmQ4yIWk40kB_8X8as-IUQCqEpaEKOYaPlqUslmy5Mqv2SL7mSIm9FmqiQdsPE_T2FT1uSr2caU8fg6JCHy5MV8bISFJfkAEY3jpRdskVqKPLRCbp7vVjzznVqrkYmbboj2E7lrmbuPeJ8ye_gVvgb33fyTbsDhbGA6ERriQFnvz23KGdtl4Y2GiSBOl_M7a-wmiWbFvgcszE13-QLvu3-bvlwCPyM4IeH6C9L1dAcZE4vGPIpKBXoSj5HoIAfzERgL0sBJoAPoctwRpBXEd46XxZ4QLh38Ne-aOjIlsREeGfJC5ZDs-iI5EWY53AMKD3XbMWdHJRRp56k6uJ1CSBZWhwfAcOugfU6_UNKVUJ6OPJro8HLQmk2nh6qSS-TBBOVZ-AqBpiKO_4mg86L42VRacFvPszolK13VR3aKMkWucqm3Ge-rkbdmOoMr522ydBnDd6N0vlc0zXKZJwa3XXuKeBxZ_zkQZVKmxrG2MEshWu4HKUMj8FLabOP3MjEsnOA-axQcxEYRgNPG43llyKqTkl4pKagigzfbUhyaJc71WqJN0w_odHNoE4HisPP8EiBLBodDKvw6kRgKmfb6we968uMHjmxY1qYkCiN_26BhPvQqW7tcbhsOxA==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c1a0000fc0feb0f_0%7C0a220b774c1d00006b072ab9_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EVEjOvsoJKF7xr3cLwZGQa3EyfMVei8Qnv6vhuEP-4WqOysOddDn0u_oe98H5sAfcUOHoDoi_i5G7YuDu-61jEYqq_Xc3Zyxbw6MVrGmZ5ve8HDCCop39xztA6l2eU9PeWOXiBtlzifJ0IJQkA90Nx-sjAynQUxmQ4yIWk40kB_8X8as-IUQCqEpaEKOYaPlqUslmy5Mqv2SL7mSIm9FmqiQdsPE_T2FT1uSr2caU8fg6JCHy5MV8bISFJfkAEY3jpRdskVqKPLRCbp7vVjzznVqrkYmbboj2E7lrmbuPeJ8ye_gVvgb33fyTbsDhbGA6ERriQFnvz23KGdtl4Y2GiSBOl_M7a-wmiWbFvgcszE13-QLvu3-bvlwCPyM4IeH6C9L1dAcZE4vGPIpKBXoSj5HoIAfzERgL0sBJoAPoctwRpBXEd46XxZ4QLh38Ne-aOjIlsREeGfJC5ZDs-iI5EWY53AMKD3XbMWdHJRRp56k6uJ1CSBZWhwfAcOugfU6_UNKVUJ6OPJro8HLQmk2nh6qSS-TBBOVZ-AqBpiKO_4mg86L42VRacFvPszolK13VR3aKMkWucqm3Ge-rkbdmOoMr522ydBnDd6N0vlc0zXKZJwa3XXuKeBxZ_zkQZVKmxrG2MEshWu4HKUMj8FLabOP3MjEsnOA-axQcxEYRgNPG43llyKqTkl4pKagigzfbUhyaJc71WqJN0w_odHNoE4HisPP8EiBLBodDKvw6kRgKmfb6we968uMHjmxY1qYkCiN_26BhPvQqW7tcbhsOxA==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-05T19:45:00.000Z", "utc_arrival": "2023-05-05T17:45:00.000Z", "local_departure": "2023-05-05T16:15:00.000Z", "utc_departure": "2023-05-05T14:15:00.000Z"}, {"id": "0b770a224bfa0000f711598b_0|0a220b774bfd0000e604e9be_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 740.29968, "distance": 1975.87, "duration": {"departure": 12600, "return": 11700, "total": 24300}, "price": 223206.4358, "conversion": {"EUR": 584.30007, "HUF": 223206.4358}, "fare": {"adults": 111603.22, "children": 111603.22, "infants": 111603.22}, "bags_price": {"1": 113.624, "2": 227.234}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 439, "hold_height": 149, "hold_length": 171, "hold_weight": 20, "hold_width": 119, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 3}, "airlines": ["W6"], "route": [{"id": "0b770a224bfa0000f711598b_0", "combination_id": "0b770a224bfa0000f711598b", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "JKREG", "fare_category": "M", "fare_classes": "J", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-03T19:45:00.000Z", "utc_arrival": "2023-04-03T17:45:00.000Z", "local_departure": "2023-04-03T16:15:00.000Z", "utc_departure": "2023-04-03T14:15:00.000Z"}, {"id": "0a220b774bfd0000e604e9be_0", "combination_id": "0a220b774bfd0000e604e9be", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-07T01:15:00.000Z", "utc_arrival": "2023-04-06T23:15:00.000Z", "local_departure": "2023-04-06T22:00:00.000Z", "utc_departure": "2023-04-06T20:00:00.000Z"}], "booking_token": "ETM4Aw1R2RYba-CVnP68zFy5i3Zpn5IaoLzRPBnmvhVRc-ijampbqL-RaW4slOpDeaYN_Slec01gjQgTto_bC7ljETv4uuWu1J-cwDLuNZR5lli7FLdYSw7vfZUHTb-CgJb807-yeWdF1BM_4e_E-bCPT-X08T3H9nYkYUwFn4hLJGox3t6IvIYvJCG0qkQgyNvXpuPZhnxKau-imyX_jKtuG30qzOxI63GOMn0Wy-8aBqAQ7LnJY6CVCoHG9zuwds-Lpa5B94vbHNyKUdeyrw5C3fwR5Xo5Du5ZntbNhuRcTg_NaIyiBHIjunzNkVs052QpjHjE-KsIuiX00Ufztg3XyX9W65pG6oL1cW0FrvKSUULJmPh-ytSPP8f992k4t_ikWhy64jYS0ms9K1ywUfq4imrZsrJDkFTPbYf5V8trcNtq-2XNpfq7AaDz_i0T-aBCA6mQcvRI7aoeX0Ko9dVaFbu1-bS-tuJKYB76ARye4LNgPcrtr-ejrQypzJuQwlkUZzTMQJwu1B6y9X37ldmqIM32AW9ajDTpI5i9sx_DYaonF4KUCb5dGOFDEuh8Msxqtea7Vrg-B-8yD2hP3PUYmvw2zPcq5kkZ9Gj52zG5N-r433caPxoKzTjYMU_0XefA4mNU2ec1KHg6S2V0uICfIXv-9KmSfL8nL-PuRZWE2cDC2RmcMuEEeg9gM5GOETam6aURsigUhkmzqBuW7KjdtDmOJ5l_jXAq0y74hcFRORY0_wcBVtDEm1795e-JsS5cDCAW6yfqRmd0VqtPFrQ==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224bfa0000f711598b_0%7C0a220b774bfd0000e604e9be_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=ETM4Aw1R2RYba-CVnP68zFy5i3Zpn5IaoLzRPBnmvhVRc-ijampbqL-RaW4slOpDeaYN_Slec01gjQgTto_bC7ljETv4uuWu1J-cwDLuNZR5lli7FLdYSw7vfZUHTb-CgJb807-yeWdF1BM_4e_E-bCPT-X08T3H9nYkYUwFn4hLJGox3t6IvIYvJCG0qkQgyNvXpuPZhnxKau-imyX_jKtuG30qzOxI63GOMn0Wy-8aBqAQ7LnJY6CVCoHG9zuwds-Lpa5B94vbHNyKUdeyrw5C3fwR5Xo5Du5ZntbNhuRcTg_NaIyiBHIjunzNkVs052QpjHjE-KsIuiX00Ufztg3XyX9W65pG6oL1cW0FrvKSUULJmPh-ytSPP8f992k4t_ikWhy64jYS0ms9K1ywUfq4imrZsrJDkFTPbYf5V8trcNtq-2XNpfq7AaDz_i0T-aBCA6mQcvRI7aoeX0Ko9dVaFbu1-bS-tuJKYB76ARye4LNgPcrtr-ejrQypzJuQwlkUZzTMQJwu1B6y9X37ldmqIM32AW9ajDTpI5i9sx_DYaonF4KUCb5dGOFDEuh8Msxqtea7Vrg-B-8yD2hP3PUYmvw2zPcq5kkZ9Gj52zG5N-r433caPxoKzTjYMU_0XefA4mNU2ec1KHg6S2V0uICfIXv-9KmSfL8nL-PuRZWE2cDC2RmcMuEEeg9gM5GOETam6aURsigUhkmzqBuW7KjdtDmOJ5l_jXAq0y74hcFRORY0_wcBVtDEm1795e-JsS5cDCAW6yfqRmd0VqtPFrQ==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-04-03T19:45:00.000Z", "utc_arrival": "2023-04-03T17:45:00.000Z", "local_departure": "2023-04-03T16:15:00.000Z", "utc_departure": "2023-04-03T14:15:00.000Z"}, {"id": "0b770a224c2f0000d0b1f5bc_0|0a220b774c33000096514b2c_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 738.672827, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 224112.9896, "conversion": {"EUR": 586.673207, "HUF": 224112.9896}, "fare": {"adults": 112056.49, "children": 112056.49, "infants": 112056.49}, "bags_price": {"1": 70.364, "2": 140.728}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 3}, "airlines": ["FR"], "route": [{"id": "0b770a224c2f0000d0b1f5bc_0", "combination_id": "0b770a224c2f0000d0b1f5bc", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-26T21:45:00.000Z", "utc_arrival": "2023-05-26T19:45:00.000Z", "local_departure": "2023-05-26T18:25:00.000Z", "utc_departure": "2023-05-26T16:25:00.000Z"}, {"id": "0a220b774c33000096514b2c_0", "combination_id": "0a220b774c33000096514b2c", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-30T14:05:00.000Z", "utc_arrival": "2023-05-30T12:05:00.000Z", "local_departure": "2023-05-30T10:55:00.000Z", "utc_departure": "2023-05-30T08:55:00.000Z"}], "booking_token": "EbMkuN9HAYF1t4OW_PpkRmDJqi_rZff2oEC3w34cPgbewUrsGjfrkYJfkSAv8CIdrJmmjwPXXKmrFzF21whmxmeK0YbhZQd9JrwuEA7DdyI_KMKusjCEIQdjnUy3wYH3YuowWEs0JJ3DKHL6cR6nuDzv14pjgAfkDge0k22C7EHR2_Rc6Bq28BQmgeemWXi_byxFGsaaS-AvG1fxZaq3yZUx1CRQFefPIMXPnkyYbkKqhKg-7397-W9P8X8sjeaAK1yBBwzakUYRHSfHOy6_U9dp9Rz-K_WVYXWEAvT_gsOxPTErELMhCsMY62nFWeJy4sHGYgCk61G-YZ0v_N7cvZbqOC3DUzENhdyAsH_VWsfK0FthPTjLwTPfRvaoZYUSbYU4-Rh0LdsSyISMhHVAYfxlpNabCplgi2Lbo5pfnmUFONGs6c3Sh5fh3LXjZ9O4kvxJ_AH1jhPGBlkTceY3-wlzlSXL2mvvgQDoLF_L80GV5Y2gy5B8jZMtzhjAs4rJelKq-NvR3oGPmaZu4BqHZDOHysl7ay-bcnbHj1auDCYCvPTN0kK8mUTiydRhie4c389u8W4CzTXor-l0RK-ggicDbQFJmn2na94AtQYcTuVIsG8h7TSW0eMeiMIXhJXRG9ikV9W_wL6tzZn4KGyQpe_UvdeLHYSK4BHc-UQ0_wKwZMxDJvS7-W703jRf81eiU4qCKbL5M7PVr8wip5PGjnw==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c2f0000d0b1f5bc_0%7C0a220b774c33000096514b2c_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EbMkuN9HAYF1t4OW_PpkRmDJqi_rZff2oEC3w34cPgbewUrsGjfrkYJfkSAv8CIdrJmmjwPXXKmrFzF21whmxmeK0YbhZQd9JrwuEA7DdyI_KMKusjCEIQdjnUy3wYH3YuowWEs0JJ3DKHL6cR6nuDzv14pjgAfkDge0k22C7EHR2_Rc6Bq28BQmgeemWXi_byxFGsaaS-AvG1fxZaq3yZUx1CRQFefPIMXPnkyYbkKqhKg-7397-W9P8X8sjeaAK1yBBwzakUYRHSfHOy6_U9dp9Rz-K_WVYXWEAvT_gsOxPTErELMhCsMY62nFWeJy4sHGYgCk61G-YZ0v_N7cvZbqOC3DUzENhdyAsH_VWsfK0FthPTjLwTPfRvaoZYUSbYU4-Rh0LdsSyISMhHVAYfxlpNabCplgi2Lbo5pfnmUFONGs6c3Sh5fh3LXjZ9O4kvxJ_AH1jhPGBlkTceY3-wlzlSXL2mvvgQDoLF_L80GV5Y2gy5B8jZMtzhjAs4rJelKq-NvR3oGPmaZu4BqHZDOHysl7ay-bcnbHj1auDCYCvPTN0kK8mUTiydRhie4c389u8W4CzTXor-l0RK-ggicDbQFJmn2na94AtQYcTuVIsG8h7TSW0eMeiMIXhJXRG9ikV9W_wL6tzZn4KGyQpe_UvdeLHYSK4BHc-UQ0_wKwZMxDJvS7-W703jRf81eiU4qCKbL5M7PVr8wip5PGjnw==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-26T21:45:00.000Z", "utc_arrival": "2023-05-26T19:45:00.000Z", "local_departure": "2023-05-26T18:25:00.000Z", "utc_departure": "2023-05-26T16:25:00.000Z"}, {"id": "0b770a224c320000850ebc30_0|0a220b774c360000ea6a6a00_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 749.304651, "distance": 1975.87, "duration": {"departure": 12600, "return": 12900, "total": 25500}, "price": 224609.0304, "conversion": {"EUR": 587.971721, "HUF": 224609.0304}, "fare": {"adults": 112304.52, "children": 112304.52, "infants": 112304.52}, "bags_price": {"1": 105.84, "2": 211.68}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 439, "hold_height": 149, "hold_length": 171, "hold_weight": 20, "hold_width": 119, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 2}, "airlines": ["W6"], "route": [{"id": "0b770a224c320000850ebc30_0", "combination_id": "0b770a224c320000850ebc30", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "GHREG", "fare_category": "M", "fare_classes": "G", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-29T19:45:00.000Z", "utc_arrival": "2023-05-29T17:45:00.000Z", "local_departure": "2023-05-29T16:15:00.000Z", "utc_departure": "2023-05-29T14:15:00.000Z"}, {"id": "0a220b774c360000ea6a6a00_0", "combination_id": "0a220b774c360000ea6a6a00", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "KREG", "fare_category": "M", "fare_classes": "K", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-03T00:05:00.000Z", "utc_arrival": "2023-06-02T22:05:00.000Z", "local_departure": "2023-06-02T20:30:00.000Z", "utc_departure": "2023-06-02T18:30:00.000Z"}], "booking_token": "E2LMn08ytqIOurpBBlmIl8eQx2uuN2Z4KB0vGDzMsqCFr7ywkpb12fbs1h2XMOG_0Dkc5wp_sPxbQeSspw_vdrQxMLqIeRU9vLTiYtNSGBJGiDpiOKzjroy6Ltc0wufjnMtWrMBKqBkZ6QSMk6-0T2E_goARjjToX0UyZDfJarOry7t35AZGy4cXzkl5yu27GWTgq9OBfiDbtv4F3OGtG4HAktiNOjgEjkdBwrNpO4xzy-cY9Al2G-SwkDbkXFQc8WXJZ_qY2CWMQ0_w9FpRH22PAtF4xP-07CclaZtaAzNc2YOP9AmaVQPXCWAhhh12E8H3S93-cwc3ypSkkOG_Am5VBtd3KWKrhxk4Olvlr-nN-6CHaZdmiKcU2GvR2CWAej1NvJtce8-YvucetM5a5ylaYWnxxQvDKxmoLAcpRTqOZy6kHoKD7-YIX_gfx2oQmm3GpA_Fr4ODEzVOFSMY-0D3LGIxrZ_WUG40xL-ldDrL9CZJp95m8tyGCZAY8n3TPEW7rpPhxl5Fb0FjK60TwQ1Xth8RdZz5rfx-jKrNcZMvlYrNJNKjDplwHlCFOk0UIpaRaBhl_pYhDXEpmG4zj_X71RLnjqXZlLfhw3FFJtiEKFxBK7_fd57TVoDoSWm7WPX82lN2mFa4zkBE7eTJI-nvHHssdA6iWD5Hw_SuPxv8oU8TBmepVCYlIcXlhfSx_B2t_F26di-MRu9NY7nmsP-8mIcE71Aa25fQCFnY3BfpZ5PAnBEWZXC-oXsHDeu0F5wvXdbyhRlKbWASEJG4-Ug==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c320000850ebc30_0%7C0a220b774c360000ea6a6a00_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=E2LMn08ytqIOurpBBlmIl8eQx2uuN2Z4KB0vGDzMsqCFr7ywkpb12fbs1h2XMOG_0Dkc5wp_sPxbQeSspw_vdrQxMLqIeRU9vLTiYtNSGBJGiDpiOKzjroy6Ltc0wufjnMtWrMBKqBkZ6QSMk6-0T2E_goARjjToX0UyZDfJarOry7t35AZGy4cXzkl5yu27GWTgq9OBfiDbtv4F3OGtG4HAktiNOjgEjkdBwrNpO4xzy-cY9Al2G-SwkDbkXFQc8WXJZ_qY2CWMQ0_w9FpRH22PAtF4xP-07CclaZtaAzNc2YOP9AmaVQPXCWAhhh12E8H3S93-cwc3ypSkkOG_Am5VBtd3KWKrhxk4Olvlr-nN-6CHaZdmiKcU2GvR2CWAej1NvJtce8-YvucetM5a5ylaYWnxxQvDKxmoLAcpRTqOZy6kHoKD7-YIX_gfx2oQmm3GpA_Fr4ODEzVOFSMY-0D3LGIxrZ_WUG40xL-ldDrL9CZJp95m8tyGCZAY8n3TPEW7rpPhxl5Fb0FjK60TwQ1Xth8RdZz5rfx-jKrNcZMvlYrNJNKjDplwHlCFOk0UIpaRaBhl_pYhDXEpmG4zj_X71RLnjqXZlLfhw3FFJtiEKFxBK7_fd57TVoDoSWm7WPX82lN2mFa4zkBE7eTJI-nvHHssdA6iWD5Hw_SuPxv8oU8TBmepVCYlIcXlhfSx_B2t_F26di-MRu9NY7nmsP-8mIcE71Aa25fQCFnY3BfpZ5PAnBEWZXC-oXsHDeu0F5wvXdbyhRlKbWASEJG4-Ug==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-29T19:45:00.000Z", "utc_arrival": "2023-05-29T17:45:00.000Z", "local_departure": "2023-05-29T16:15:00.000Z", "utc_departure": "2023-05-29T14:15:00.000Z"}, {"id": "0b770a224c470000f72dd482_0|0a220b774c4b0000625e6e09_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 743.358741, "distance": 1975.87, "duration": {"departure": 12600, "return": 11400, "total": 24000}, "price": 224884.3578, "conversion": {"EUR": 588.692461, "HUF": 224884.3578}, "fare": {"adults": 112442.18, "children": 112442.18, "infants": 112442.18}, "bags_price": {"1": 100.114, "2": 210.042}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 158, "hold_height": 52, "hold_length": 78, "hold_weight": 20, "hold_width": 28, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 3, "personal_item_width": 15}, "availability": {"seats": 4}, "airlines": ["W6", "IB"], "route": [{"id": "0b770a224c470000f72dd482_0", "combination_id": "0b770a224c470000f72dd482", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-19T19:45:00.000Z", "utc_arrival": "2023-06-19T17:45:00.000Z", "local_departure": "2023-06-19T16:15:00.000Z", "utc_departure": "2023-06-19T14:15:00.000Z"}, {"id": "0a220b774c4b0000625e6e09_0", "combination_id": "0a220b774c4b0000625e6e09", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "IB", "flight_no": 3278, "operating_carrier": "IB", "operating_flight_no": "3278", "fare_basis": "QWNNAOB4", "fare_category": "M", "fare_classes": "Q", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-23T14:55:00.000Z", "utc_arrival": "2023-06-23T12:55:00.000Z", "local_departure": "2023-06-23T11:45:00.000Z", "utc_departure": "2023-06-23T09:45:00.000Z"}], "booking_token": "EThHbagALQl2dUE0AjmqZn2X-pVT6bxiSRHdz4UUQqGaxTBqKaxSj5Qd6I_inKw_2zDbmGVpbmer4m5AUHLCEnhkNlqmtYhNmvBlXInNLwqvneFeNpVpUWg_36KqKpYVeVkqajwwsmWW9DW7ccylVHPnGD6Lho9-Mwg4dqWm_JdovvUv-OEG68HLcQ42dKTiL2pFJEJ2hz3ZVXFbvjZewk2WP3fW55XYlrcKB87ICm6bJszfGdJ9HxysgSBL7dvQTeNWEcjBbvBFZXAyRjzU9gJuRPuTZs_7X4ysTt0eRYcyMnXKmk5mDprspnxCuAtgUH5Co6Hy2iF7R1mpfzWZQt5j5rqfQ5j1UJaupOjT3fn24V15gdCREEJlz5MW3ktdTeftrwxaL_SpB7l98_Ntuw7BWvwz5pBtg8fWSyTsAD5FSFdRMqJe3VrtQrBIjXUJZ3IBgL59iuLO9AY9lb1OCzXQDBBy4SKaJrD-3gGIB9_FEmstBaTl_xDDtdA3SIAcglcfUB5LXvmnyOTf5SopWJ81vfpoQJ59qpb4vO2_qLdGjkWlv6IjVfEAHAt4R1K65kV46TpM49-lNBDIfQqTpGlCw_Odw1em0j_GNH9jFKNJCXP7oMllIabyDE5_bmpXjpJBXl0LshARn5PuR2YekyZVAkJUTPXwe0U5X09wk36vT5LHM8YZjdLDJvQRjOqOYLiKlvI2O3q1rydBUewiPtchuZEvW1h5gr8DvvCrhz5usfnWOW7vFCBeahJOJjeIKHyMFkJkFeo-f9dp-LSlLD8NQWiaZ-jmfbRJC_qCtMpMyq8qZ1p0gwqP_476lCJ48", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c470000f72dd482_0%7C0a220b774c4b0000625e6e09_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EThHbagALQl2dUE0AjmqZn2X-pVT6bxiSRHdz4UUQqGaxTBqKaxSj5Qd6I_inKw_2zDbmGVpbmer4m5AUHLCEnhkNlqmtYhNmvBlXInNLwqvneFeNpVpUWg_36KqKpYVeVkqajwwsmWW9DW7ccylVHPnGD6Lho9-Mwg4dqWm_JdovvUv-OEG68HLcQ42dKTiL2pFJEJ2hz3ZVXFbvjZewk2WP3fW55XYlrcKB87ICm6bJszfGdJ9HxysgSBL7dvQTeNWEcjBbvBFZXAyRjzU9gJuRPuTZs_7X4ysTt0eRYcyMnXKmk5mDprspnxCuAtgUH5Co6Hy2iF7R1mpfzWZQt5j5rqfQ5j1UJaupOjT3fn24V15gdCREEJlz5MW3ktdTeftrwxaL_SpB7l98_Ntuw7BWvwz5pBtg8fWSyTsAD5FSFdRMqJe3VrtQrBIjXUJZ3IBgL59iuLO9AY9lb1OCzXQDBBy4SKaJrD-3gGIB9_FEmstBaTl_xDDtdA3SIAcglcfUB5LXvmnyOTf5SopWJ81vfpoQJ59qpb4vO2_qLdGjkWlv6IjVfEAHAt4R1K65kV46TpM49-lNBDIfQqTpGlCw_Odw1em0j_GNH9jFKNJCXP7oMllIabyDE5_bmpXjpJBXl0LshARn5PuR2YekyZVAkJUTPXwe0U5X09wk36vT5LHM8YZjdLDJvQRjOqOYLiKlvI2O3q1rydBUewiPtchuZEvW1h5gr8DvvCrhz5usfnWOW7vFCBeahJOJjeIKHyMFkJkFeo-f9dp-LSlLD8NQWiaZ-jmfbRJC_qCtMpMyq8qZ1p0gwqP_476lCJ48", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-19T19:45:00.000Z", "utc_arrival": "2023-06-19T17:45:00.000Z", "local_departure": "2023-06-19T16:15:00.000Z", "utc_departure": "2023-06-19T14:15:00.000Z"}, {"id": "0b770a224c4a0000c81c2b63_0|0a220b774c4e0000de14d559_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 741.012015, "distance": 1975.87, "duration": {"departure": 11700, "return": 11700, "total": 23400}, "price": 225006.5747, "conversion": {"EUR": 589.012395, "HUF": 225006.5747}, "fare": {"adults": 112503.29, "children": 115235.01, "infants": 115235.01}, "bags_price": {"1": 97.118, "2": 204.036}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 158, "hold_height": 52, "hold_length": 78, "hold_weight": 20, "hold_width": 28, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 3, "personal_item_width": 15}, "availability": {"seats": 7}, "airlines": ["W6", "IB"], "route": [{"id": "0b770a224c4a0000c81c2b63_0", "combination_id": "0b770a224c4a0000c81c2b63", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "IB", "flight_no": 3279, "operating_carrier": "IB", "operating_flight_no": "3279", "fare_basis": "ODNNAOB4", "fare_category": "M", "fare_classes": "O", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-22T18:50:00.000Z", "utc_arrival": "2023-06-22T16:50:00.000Z", "local_departure": "2023-06-22T15:35:00.000Z", "utc_departure": "2023-06-22T13:35:00.000Z"}, {"id": "0a220b774c4e0000de14d559_0", "combination_id": "0a220b774c4e0000de14d559", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IJREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-26T23:45:00.000Z", "utc_arrival": "2023-06-26T21:45:00.000Z", "local_departure": "2023-06-26T20:30:00.000Z", "utc_departure": "2023-06-26T18:30:00.000Z"}], "booking_token": "Eub52ESdhXo8reqRWefNHbgVApfM74-OFiQa-aECb2eCmVX0YqNze4u7A0ZH4dWBBMQk4GEJt1ej_wuoJAYBFjrO-1jNlLyfod9uJyevf-JeLx9yFUdA7fvWHtuVTDyh7yMiB4x8VnUV-mWamTw34XDoS04B5JdwwrmbfmvOIfZI5bkaW4DSC-Qgtz5mST-V8vAxh8WPhfIiP80AVXV3v_40Gg4LAB6Z_xNP7kDs16H-J0CqJfDb8T48yXxssqTFtGQuvcRmRX0z_jwtSUbm4wZKJ53heQaWaJcfOC4yGRL5NxNivNmWif1bqe9QzEUBr7ejaAECihTmtJRanhL1IvEADtCew3yOuzmAssYaZa7GxAfDkISEsV1MYUY8TJvGdi98rshJWoxOxu6GGlYyiZsyUzccQwK2fV46YF5aN7skl2VUSeLK13NBbh3Kd0OUb8mZ0ATmZfPDT-yyXrbT0dj7zYnczI2m9wHHC3MCFehlRkl32Ao9bBoAJOJ2HjZjyzUKjjet_TpWTwkQNVZaY2jKHaVZUxUdUTwgCQRUa5bnkfP8ZonC5JRDkpOSTcmotl455_bXrAOVtbRTtzzaY5C8h0gbh3HFzFj4pL_MfiwK7sAJri0M7KlbbfFBQJWdNovrFIT3exRwKElyelybFaT23rDKJLulhOZYJKrSTcRFZcs9F-8_2F883f8EYMDwrKZFmaMO8Me3mVgOmaJLSpkYcYx-j9pWHQc1Q7suiyJLYRA_IhpuvRwHFUGUHx7afvUBVhhLz89xLlKv94LxddMw3YILIJq3mYqSv-XD1IAmhgzb4NBNksfcwQqlxO7ntCOeVzZf9i0NQ_eu6vq2bVA==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c4a0000c81c2b63_0%7C0a220b774c4e0000de14d559_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=Eub52ESdhXo8reqRWefNHbgVApfM74-OFiQa-aECb2eCmVX0YqNze4u7A0ZH4dWBBMQk4GEJt1ej_wuoJAYBFjrO-1jNlLyfod9uJyevf-JeLx9yFUdA7fvWHtuVTDyh7yMiB4x8VnUV-mWamTw34XDoS04B5JdwwrmbfmvOIfZI5bkaW4DSC-Qgtz5mST-V8vAxh8WPhfIiP80AVXV3v_40Gg4LAB6Z_xNP7kDs16H-J0CqJfDb8T48yXxssqTFtGQuvcRmRX0z_jwtSUbm4wZKJ53heQaWaJcfOC4yGRL5NxNivNmWif1bqe9QzEUBr7ejaAECihTmtJRanhL1IvEADtCew3yOuzmAssYaZa7GxAfDkISEsV1MYUY8TJvGdi98rshJWoxOxu6GGlYyiZsyUzccQwK2fV46YF5aN7skl2VUSeLK13NBbh3Kd0OUb8mZ0ATmZfPDT-yyXrbT0dj7zYnczI2m9wHHC3MCFehlRkl32Ao9bBoAJOJ2HjZjyzUKjjet_TpWTwkQNVZaY2jKHaVZUxUdUTwgCQRUa5bnkfP8ZonC5JRDkpOSTcmotl455_bXrAOVtbRTtzzaY5C8h0gbh3HFzFj4pL_MfiwK7sAJri0M7KlbbfFBQJWdNovrFIT3exRwKElyelybFaT23rDKJLulhOZYJKrSTcRFZcs9F-8_2F883f8EYMDwrKZFmaMO8Me3mVgOmaJLSpkYcYx-j9pWHQc1Q7suiyJLYRA_IhpuvRwHFUGUHx7afvUBVhhLz89xLlKv94LxddMw3YILIJq3mYqSv-XD1IAmhgzb4NBNksfcwQqlxO7ntCOeVzZf9i0NQ_eu6vq2bVA==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-22T18:50:00.000Z", "utc_arrival": "2023-06-22T16:50:00.000Z", "local_departure": "2023-06-22T15:35:00.000Z", "utc_departure": "2023-06-22T13:35:00.000Z"}, {"id": "0b770a224c36000074fbf6e5_0|0a220b774c390000563d5408_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 745.488176, "distance": 1975.87, "duration": {"departure": 12600, "return": 11700, "total": 24300}, "price": 225188.4751, "conversion": {"EUR": 589.488566, "HUF": 225188.4751}, "fare": {"adults": 112594.24, "children": 115777.56, "infants": 115777.56}, "bags_price": {"1": 117.348, "2": 234.696}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 439, "hold_height": 149, "hold_length": 171, "hold_weight": 20, "hold_width": 119, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 5}, "airlines": ["W6"], "route": [{"id": "0b770a224c36000074fbf6e5_0", "combination_id": "0b770a224c36000074fbf6e5", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-02T19:45:00.000Z", "utc_arrival": "2023-06-02T17:45:00.000Z", "local_departure": "2023-06-02T16:15:00.000Z", "utc_departure": "2023-06-02T14:15:00.000Z"}, {"id": "0a220b774c390000563d5408_0", "combination_id": "0a220b774c390000563d5408", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-05T23:45:00.000Z", "utc_arrival": "2023-06-05T21:45:00.000Z", "local_departure": "2023-06-05T20:30:00.000Z", "utc_departure": "2023-06-05T18:30:00.000Z"}], "booking_token": "EnNRgqKvpWWLsjQPldYmvilFeNcCAfxFMNweNnqcn2xTWCS9qScN6Xu-frn4Gmvv3aWbg4e8W0idETaQnnaucPRvl2TcEtSg7dYPW_5NzEjXsMVYeKgFCS_kDMKdFTBlWTTTVC8ln_KGaIQHz19YvdNthql8Nkp3F5UoEcD6pf9JkWtvdKzUvO_nWwRKJdNzb4M3Fe8CgcbpRgWfE2jL__--5QxIcdGIWFO4GZZMdUBfwqCSua0FsAVNM-l4Jg-N368sxZGAKe32pEszBfrG29RiJn9V61WQ7l3aD5mXeXufKVNZyJSbqT048vcByx6ht1ICDm_GvFhwCS54Me0PWpVWNGOEEXoUAiVhwD6E8EX6F7c7AE_uYauVCuGu7mcGYBiOpC-v1RKsfn1ZygZVWAfPS_02S5_Kh246VWZKSaBtLyNg6O46JOZwwnav45JidJaL0cdyj43pCAwkCbFL7HVtcCRpDcRIz67HRj9WWCD9BNi2EZRGCOWH89o_7NL-B3tf05O5Ulm-9mrRUkNdW2BnYyVQ5U_YPqOJ4FDsueh4e4HZMRTZ7GlHU2iqMMu9ctHeugtPxzfiDhUwzDgV4qEwhaE-QsHoqnFEf4jPL7dvqtCjT66K3dWa1gR6bNFX1sreiCfrRJ1Ui0b7L5s2hmzcALbeP-e8x5-06R89YZIfzhr_M-kMTd9nE2kN0t4_XQRL5Ubh3mPB1sCC8hdyDDj_LhfOB8SxHyVm_Xc66-1vkHIThbfdl7g_M1TrWSTA621X2z7ircecDub5z2-vtqw==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c36000074fbf6e5_0%7C0a220b774c390000563d5408_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EnNRgqKvpWWLsjQPldYmvilFeNcCAfxFMNweNnqcn2xTWCS9qScN6Xu-frn4Gmvv3aWbg4e8W0idETaQnnaucPRvl2TcEtSg7dYPW_5NzEjXsMVYeKgFCS_kDMKdFTBlWTTTVC8ln_KGaIQHz19YvdNthql8Nkp3F5UoEcD6pf9JkWtvdKzUvO_nWwRKJdNzb4M3Fe8CgcbpRgWfE2jL__--5QxIcdGIWFO4GZZMdUBfwqCSua0FsAVNM-l4Jg-N368sxZGAKe32pEszBfrG29RiJn9V61WQ7l3aD5mXeXufKVNZyJSbqT048vcByx6ht1ICDm_GvFhwCS54Me0PWpVWNGOEEXoUAiVhwD6E8EX6F7c7AE_uYauVCuGu7mcGYBiOpC-v1RKsfn1ZygZVWAfPS_02S5_Kh246VWZKSaBtLyNg6O46JOZwwnav45JidJaL0cdyj43pCAwkCbFL7HVtcCRpDcRIz67HRj9WWCD9BNi2EZRGCOWH89o_7NL-B3tf05O5Ulm-9mrRUkNdW2BnYyVQ5U_YPqOJ4FDsueh4e4HZMRTZ7GlHU2iqMMu9ctHeugtPxzfiDhUwzDgV4qEwhaE-QsHoqnFEf4jPL7dvqtCjT66K3dWa1gR6bNFX1sreiCfrRJ1Ui0b7L5s2hmzcALbeP-e8x5-06R89YZIfzhr_M-kMTd9nE2kN0t4_XQRL5Ubh3mPB1sCC8hdyDDj_LhfOB8SxHyVm_Xc66-1vkHIThbfdl7g_M1TrWSTA621X2z7ircecDub5z2-vtqw==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-02T19:45:00.000Z", "utc_arrival": "2023-06-02T17:45:00.000Z", "local_departure": "2023-06-02T16:15:00.000Z", "utc_departure": "2023-06-02T14:15:00.000Z"}, {"id": "0b770a224c4100007151a3a5_0|0a220b774c450000e23fa8bd_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 741.806011, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 225309.8863, "conversion": {"EUR": 589.806391, "HUF": 225309.8863}, "fare": {"adults": 112654.94, "children": 112654.94, "infants": 112654.94}, "bags_price": {"1": 74.382, "2": 158.382}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 158, "hold_height": 52, "hold_length": 78, "hold_weight": 20, "hold_width": 28, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 3, "personal_item_width": 15}, "availability": {"seats": 2}, "airlines": ["FR", "IB"], "route": [{"id": "0b770a224c4100007151a3a5_0", "combination_id": "0b770a224c4100007151a3a5", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-13T10:15:00.000Z", "utc_arrival": "2023-06-13T08:15:00.000Z", "local_departure": "2023-06-13T06:55:00.000Z", "utc_departure": "2023-06-13T04:55:00.000Z"}, {"id": "0a220b774c450000e23fa8bd_0", "combination_id": "0a220b774c450000e23fa8bd", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "IB", "flight_no": 3278, "operating_carrier": "IB", "operating_flight_no": "3278", "fare_basis": "SDNNAOB4", "fare_category": "M", "fare_classes": "S", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-17T14:55:00.000Z", "utc_arrival": "2023-06-17T12:55:00.000Z", "local_departure": "2023-06-17T11:45:00.000Z", "utc_departure": "2023-06-17T09:45:00.000Z"}], "booking_token": "EW-aQroq7HVxth1JGNbL02MFqFPMDZvM6yNcOMd7UMyt81xM4fIUDKusDv16V9F5j-l38XCBGZusGQfj7ydGG2JPvIiZMTDL_wW8GjbmQKX1AoBPNLQbYElIIQKWjHt_OZJoUbxXry7vbF_pV2kLKLlB6DQuauqqPDXAQJzAP3QvlNQme6_YcrRcrikQdXqpcCp2fUb8wcB86DePVtys67kA_eyb8XYeyJFlaQL6hmXDh_f6aYtrfakbIHn9UHB5c7I8GhBShbyrPfxcUq5SM3dFSyQuaubAyFwkgV8Iz8tgI5CWvCoFllvHaBbowAW1cOMNCOVlPBP-XSeWLC3WNO68Dh0w70uAi4dOvbkWkTI1ajVZmXPv6gnKziotg6sTYQjb7lLQWcl1PtxsJcb_dXo2IuyPN3eu-7TIQBCGSl8sdX4ZhSokyBY88r_IG6yJd14aAjyUb1nT9Oq2bPc78g-TghAueswAdy_w62puneUVIefwoTk6C9wHG876DGxn_cEzIi4cn-sl19Uv_pHe3PwsyYwH3I1LPhRvVymIP7hZRgFwszodtTbAX0Grdnpz88LH5lG1jaU-IjIEa8P7VIu5QKvcpgv3hiNZq-KcdmKMM41vAVrenIDOZ83bInLWtFcYuTuoUU7RcAW8I528xJnrxf75E6p0x7GBeF2dVrv2QPxXu9kGk51YibJmdgefU4MYY2o4g_QV-DrdjdtKW4DJM4bbsRyXS9p3pBWy71SEcO5Y_AU_E1K-mIEMYW1aObM2wIGsbYkSSxY1g1QwgPIkElQk3k0-L__5nUrdrTUQ=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c4100007151a3a5_0%7C0a220b774c450000e23fa8bd_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EW-aQroq7HVxth1JGNbL02MFqFPMDZvM6yNcOMd7UMyt81xM4fIUDKusDv16V9F5j-l38XCBGZusGQfj7ydGG2JPvIiZMTDL_wW8GjbmQKX1AoBPNLQbYElIIQKWjHt_OZJoUbxXry7vbF_pV2kLKLlB6DQuauqqPDXAQJzAP3QvlNQme6_YcrRcrikQdXqpcCp2fUb8wcB86DePVtys67kA_eyb8XYeyJFlaQL6hmXDh_f6aYtrfakbIHn9UHB5c7I8GhBShbyrPfxcUq5SM3dFSyQuaubAyFwkgV8Iz8tgI5CWvCoFllvHaBbowAW1cOMNCOVlPBP-XSeWLC3WNO68Dh0w70uAi4dOvbkWkTI1ajVZmXPv6gnKziotg6sTYQjb7lLQWcl1PtxsJcb_dXo2IuyPN3eu-7TIQBCGSl8sdX4ZhSokyBY88r_IG6yJd14aAjyUb1nT9Oq2bPc78g-TghAueswAdy_w62puneUVIefwoTk6C9wHG876DGxn_cEzIi4cn-sl19Uv_pHe3PwsyYwH3I1LPhRvVymIP7hZRgFwszodtTbAX0Grdnpz88LH5lG1jaU-IjIEa8P7VIu5QKvcpgv3hiNZq-KcdmKMM41vAVrenIDOZ83bInLWtFcYuTuoUU7RcAW8I528xJnrxf75E6p0x7GBeF2dVrv2QPxXu9kGk51YibJmdgefU4MYY2o4g_QV-DrdjdtKW4DJM4bbsRyXS9p3pBWy71SEcO5Y_AU_E1K-mIEMYW1aObM2wIGsbYkSSxY1g1QwgPIkElQk3k0-L__5nUrdrTUQ=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-13T10:15:00.000Z", "utc_arrival": "2023-06-13T08:15:00.000Z", "local_departure": "2023-06-13T06:55:00.000Z", "utc_departure": "2023-06-13T04:55:00.000Z"}, {"id": "0b770a224c3c0000c3c77655_0|0a220b774c3f00004d959dc4_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 746.440712, "distance": 1975.87, "duration": {"departure": 12600, "return": 11700, "total": 24300}, "price": 225552.35, "conversion": {"EUR": 590.441102, "HUF": 225552.35}, "fare": {"adults": 112776.18, "children": 116032.95, "infants": 116032.95}, "bags_price": {"1": 105.924, "2": 211.848}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 439, "hold_height": 149, "hold_length": 171, "hold_weight": 20, "hold_width": 119, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 2}, "airlines": ["W6"], "route": [{"id": "0b770a224c3c0000c3c77655_0", "combination_id": "0b770a224c3c0000c3c77655", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "HIREG", "fare_category": "M", "fare_classes": "H", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-08T21:15:00.000Z", "utc_arrival": "2023-06-08T19:15:00.000Z", "local_departure": "2023-06-08T17:45:00.000Z", "utc_departure": "2023-06-08T15:45:00.000Z"}, {"id": "0a220b774c3f00004d959dc4_0", "combination_id": "0a220b774c3f00004d959dc4", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IJREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-11T21:05:00.000Z", "utc_arrival": "2023-06-11T19:05:00.000Z", "local_departure": "2023-06-11T17:50:00.000Z", "utc_departure": "2023-06-11T15:50:00.000Z"}], "booking_token": "EO-CBX6vwoF750cASP2SHIqjIfRc-4v_Hb5WTMsFYOdAelFXVkZnBgg-PAJya9j_6F_RrmFxgOinAgg9zdtzxseEAs_5WnKLpQWmN7rvNUp23ItIFyyIoe3ILHTSKmNis4Toi64nx6COaMT1HSSOeaq_3d4ZGvmZySXLMbfLJWd9qk-MqirDJDA_wGmMK5GsvfU9wN3Dj5252f9EE0UslSwLwwYYlzMtAJSkezsfDcNVLL2Re4xL4ZcfvvqrnTexMOE9ftJnGISMGm1hruQ_zqwsZ2ICDmMtBOPMNLel2eouFZAwJRSbnJaZLNJq4IIibSpCJdyjFpb6DAf9fWSlczQxOOS0ITmX-zGqC0areT_Opwccj45JI5OzPexSXNM-x3BrRChBiazX5fuORWTddHz2skuYfgfPGNkSzNAsX9BDP_FCLRQxwQmrtmG88NOhLnVkoOb453WnThPA629X9-_5hWLaYk2Qz2InU5Gutf_X7qgbl22B9aUc5rfTn4y9Zq0Mm4jqzGwUprOD40YYmOiY38_ijQAfJmaaAPfA-mqIUyxeWB7MiUHZW7feLE1CKCk67IQmPUjpwyPtbVm8clH6WddKUDZHtHZJPPB2GPehTVnzkBF5s5_fn0wFXmhZBeN57ziTRMxJr_eRT8-L0rI-8vUPZFgwFxzqFPQC-AKA5BXXzztO__WqCp7t_hHOn2M24IzdjOViGUyotHcX2Q7zjqZl9fmKd4kI2nkpjfDjfbyJZxFDU4kYB0WoYz0hGYSFC58lcgGDO3KCHBectXLoNTahDwutfUKqjI2e0fkGyzpB60cVjkkptHpDFoPaI", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c3c0000c3c77655_0%7C0a220b774c3f00004d959dc4_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EO-CBX6vwoF750cASP2SHIqjIfRc-4v_Hb5WTMsFYOdAelFXVkZnBgg-PAJya9j_6F_RrmFxgOinAgg9zdtzxseEAs_5WnKLpQWmN7rvNUp23ItIFyyIoe3ILHTSKmNis4Toi64nx6COaMT1HSSOeaq_3d4ZGvmZySXLMbfLJWd9qk-MqirDJDA_wGmMK5GsvfU9wN3Dj5252f9EE0UslSwLwwYYlzMtAJSkezsfDcNVLL2Re4xL4ZcfvvqrnTexMOE9ftJnGISMGm1hruQ_zqwsZ2ICDmMtBOPMNLel2eouFZAwJRSbnJaZLNJq4IIibSpCJdyjFpb6DAf9fWSlczQxOOS0ITmX-zGqC0areT_Opwccj45JI5OzPexSXNM-x3BrRChBiazX5fuORWTddHz2skuYfgfPGNkSzNAsX9BDP_FCLRQxwQmrtmG88NOhLnVkoOb453WnThPA629X9-_5hWLaYk2Qz2InU5Gutf_X7qgbl22B9aUc5rfTn4y9Zq0Mm4jqzGwUprOD40YYmOiY38_ijQAfJmaaAPfA-mqIUyxeWB7MiUHZW7feLE1CKCk67IQmPUjpwyPtbVm8clH6WddKUDZHtHZJPPB2GPehTVnzkBF5s5_fn0wFXmhZBeN57ziTRMxJr_eRT8-L0rI-8vUPZFgwFxzqFPQC-AKA5BXXzztO__WqCp7t_hHOn2M24IzdjOViGUyotHcX2Q7zjqZl9fmKd4kI2nkpjfDjfbyJZxFDU4kYB0WoYz0hGYSFC58lcgGDO3KCHBectXLoNTahDwutfUKqjI2e0fkGyzpB60cVjkkptHpDFoPaI", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-08T21:15:00.000Z", "utc_arrival": "2023-06-08T19:15:00.000Z", "local_departure": "2023-06-08T17:45:00.000Z", "utc_departure": "2023-06-08T15:45:00.000Z"}, {"id": "0b770a224c36000074fbf6e5_0|0a220b774c3a0000b5d31f3b_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 745.737714, "distance": 1975.87, "duration": {"departure": 12600, "return": 11400, "total": 24000}, "price": 225793.141, "conversion": {"EUR": 591.071434, "HUF": 225793.141}, "fare": {"adults": 112896.57, "children": 112896.57, "infants": 112896.57}, "bags_price": {"1": 95.844, "2": 191.688}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 5}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224c36000074fbf6e5_0", "combination_id": "0b770a224c36000074fbf6e5", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-02T19:45:00.000Z", "utc_arrival": "2023-06-02T17:45:00.000Z", "local_departure": "2023-06-02T16:15:00.000Z", "utc_departure": "2023-06-02T14:15:00.000Z"}, {"id": "0a220b774c3a0000b5d31f3b_0", "combination_id": "0a220b774c3a0000b5d31f3b", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-06T14:05:00.000Z", "utc_arrival": "2023-06-06T12:05:00.000Z", "local_departure": "2023-06-06T10:55:00.000Z", "utc_departure": "2023-06-06T08:55:00.000Z"}], "booking_token": "EaD2fNWnIgPskuN-oECmnGXhVsKe1ZtJz1wIltgdNqXdDrUE2ssjLdY_ad33B5-EXqooB3vvXQbDA3vrUdNSveGqAQH7qBsgPHopDJpupt-u6r1gJkWLRUBlQXnCMQEGDvGYNSzx160AtXJia_WV03qnHCLTYlIxmIXa00wGX3Ws1cQEBt_NBFLJAKXCxtVjhYWJh27xyT3x3QT_ZdbtnJl6TtU6KfIQ8jH7uFztbflvxiaos59OY4ERF426YZ2UuoSVSbMHDhNN3MS0BHyxoIhMtkbGeONOPbgksqy4h19gNP0a3n17jjQ0y1RF4JTu66IKaePajVIDHoei6isKODvgqeVmcl2qtg8PPKbGHx4Wzd9_jO38VAKBrea0pJ3KtBkrtBIchRSOh33I_-M32c54z9rSGmt4OXj0drGAmFdFiI7xMDv9vu3-C8lcKvXLeS2UTNRhroCoO-M8iGlClG4w5C2ugnIxrFV4fmtzvLl5mP5oUrmQOKa58nqLpR9KbuJ27IzNHicHn0Pm66IFFpWlwVhcD4NNkhRTS5FmRzMWASO84v-zQet40T8L_jiwXnwVqPkJsLN1Xo64bzgcKJ1TOB138HCOzcZwqscMNLopOYOvIHL0wZdenJAL1SFHQcEYDj0FplHrJJMPv7YFqaJMgd79xcQwr0v71nKKJB8M9QSjAcTqUOuLkz360ZJzNwdGs5IYib3y-pz21BgLAUi_RiBZdR0IVfG4ciop2PpGZvU21HA7xj7WDu9LQHbRsxXQWkZ6uVZTWWOv24KmSiA==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c36000074fbf6e5_0%7C0a220b774c3a0000b5d31f3b_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EaD2fNWnIgPskuN-oECmnGXhVsKe1ZtJz1wIltgdNqXdDrUE2ssjLdY_ad33B5-EXqooB3vvXQbDA3vrUdNSveGqAQH7qBsgPHopDJpupt-u6r1gJkWLRUBlQXnCMQEGDvGYNSzx160AtXJia_WV03qnHCLTYlIxmIXa00wGX3Ws1cQEBt_NBFLJAKXCxtVjhYWJh27xyT3x3QT_ZdbtnJl6TtU6KfIQ8jH7uFztbflvxiaos59OY4ERF426YZ2UuoSVSbMHDhNN3MS0BHyxoIhMtkbGeONOPbgksqy4h19gNP0a3n17jjQ0y1RF4JTu66IKaePajVIDHoei6isKODvgqeVmcl2qtg8PPKbGHx4Wzd9_jO38VAKBrea0pJ3KtBkrtBIchRSOh33I_-M32c54z9rSGmt4OXj0drGAmFdFiI7xMDv9vu3-C8lcKvXLeS2UTNRhroCoO-M8iGlClG4w5C2ugnIxrFV4fmtzvLl5mP5oUrmQOKa58nqLpR9KbuJ27IzNHicHn0Pm66IFFpWlwVhcD4NNkhRTS5FmRzMWASO84v-zQet40T8L_jiwXnwVqPkJsLN1Xo64bzgcKJ1TOB138HCOzcZwqscMNLopOYOvIHL0wZdenJAL1SFHQcEYDj0FplHrJJMPv7YFqaJMgd79xcQwr0v71nKKJB8M9QSjAcTqUOuLkz360ZJzNwdGs5IYib3y-pz21BgLAUi_RiBZdR0IVfG4ciop2PpGZvU21HA7xj7WDu9LQHbRsxXQWkZ6uVZTWWOv24KmSiA==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-02T19:45:00.000Z", "utc_arrival": "2023-06-02T17:45:00.000Z", "local_departure": "2023-06-02T16:15:00.000Z", "utc_departure": "2023-06-02T14:15:00.000Z"}, {"id": "0b770a224c0b000076bbcc9c_0|0a220b774c0f00005b6aa57a_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 743.751097, "distance": 1975.87, "duration": {"departure": 11700, "return": 11700, "total": 23400}, "price": 226052.9218, "conversion": {"EUR": 591.751477, "HUF": 226052.9218}, "fare": {"adults": 113026.46, "children": 115513.73, "infants": 115513.73}, "bags_price": {"1": 67.9, "2": 145.6}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 158, "hold_height": 52, "hold_length": 78, "hold_weight": 20, "hold_width": 28, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 3, "personal_item_width": 15}, "availability": {"seats": 7}, "airlines": ["W6", "IB"], "route": [{"id": "0b770a224c0b000076bbcc9c_0", "combination_id": "0b770a224c0b000076bbcc9c", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "IB", "flight_no": 3279, "operating_carrier": "IB", "operating_flight_no": "3279", "fare_basis": "QDNNAOB4", "fare_category": "M", "fare_classes": "Q", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-20T18:50:00.000Z", "utc_arrival": "2023-04-20T16:50:00.000Z", "local_departure": "2023-04-20T15:35:00.000Z", "utc_departure": "2023-04-20T13:35:00.000Z"}, {"id": "0a220b774c0f00005b6aa57a_0", "combination_id": "0a220b774c0f00005b6aa57a", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IJREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-24T23:45:00.000Z", "utc_arrival": "2023-04-24T21:45:00.000Z", "local_departure": "2023-04-24T20:30:00.000Z", "utc_departure": "2023-04-24T18:30:00.000Z"}], "booking_token": "ErE1jDoAihrrtFZVuSCsmbFykYNGgeZ2iFNqsdYcHNeKZi5pdUQqth6TiFDBQ61urwmsPRY4idvzsTzcDQkhxQMQRiGIR2tUVqKYCY7LDygjG28R3T0EY9X42qazAlILKYx68DM25N8hxfw1GOA0lE5YR1FWsNdBP1agoK6gzeV05v5-Ka2EJEBADrPWSmAo19vw0jFXbtHPqpHnAA94Y_ccnz-2rfHmyq8ziLillmsUK4tNz8W3uRMf7MZ51XX0nStaMac5sF-okTJm7C1l0GjB_OnTWgzW0-ZwCrGuKRTiM6tux6ye3j9X2qAVzqYeM3Q9faMksxAbbqA5o-VCY5ln4ZyqsFkLWW6qQr6iHA7yRnIqHtvQOtlDkIcvyHONGAFytJXzUEtmFbYj7dHgcvWgINJWJCV8e_jiOYhSxtEmnLI1RCSfQSs6uJfXoSFuHzI4P7F93eQNlwDnybH8Ogmmtd2uXdD7xodw2fjWEkH25uBKPTOGybuig0tX8sNtdguMOvOZ4m2xcFZRLMwV8eu9H2kg5ZaDhK7DhzNufXuO-ToZqaWOHk6Ppg3y3Z_bezCV7dDL-XPMxy1ir8q4Mc1Xy2vVJ8F7oGfc68h1dlIqmVXsJUSysn4nApPkXdeVtR_9Phg8MNCZWlNNSxBSNqwIzvht3txXG-Brfl125UXMsoyRNgdE1OosphfzGaCiKH82wpKAzfAK1pbh8rwQBTRqJIKfARFcHOe4xn7Q0fXiFEW0CVIMYKY-d0s7oLvZ4vfJrw5oAPbw5OVmQOfjwt0oKT4Zl2z9VCeP6g017lk3hJUpDNFuoOw5cDE4ZaxfH", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c0b000076bbcc9c_0%7C0a220b774c0f00005b6aa57a_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=ErE1jDoAihrrtFZVuSCsmbFykYNGgeZ2iFNqsdYcHNeKZi5pdUQqth6TiFDBQ61urwmsPRY4idvzsTzcDQkhxQMQRiGIR2tUVqKYCY7LDygjG28R3T0EY9X42qazAlILKYx68DM25N8hxfw1GOA0lE5YR1FWsNdBP1agoK6gzeV05v5-Ka2EJEBADrPWSmAo19vw0jFXbtHPqpHnAA94Y_ccnz-2rfHmyq8ziLillmsUK4tNz8W3uRMf7MZ51XX0nStaMac5sF-okTJm7C1l0GjB_OnTWgzW0-ZwCrGuKRTiM6tux6ye3j9X2qAVzqYeM3Q9faMksxAbbqA5o-VCY5ln4ZyqsFkLWW6qQr6iHA7yRnIqHtvQOtlDkIcvyHONGAFytJXzUEtmFbYj7dHgcvWgINJWJCV8e_jiOYhSxtEmnLI1RCSfQSs6uJfXoSFuHzI4P7F93eQNlwDnybH8Ogmmtd2uXdD7xodw2fjWEkH25uBKPTOGybuig0tX8sNtdguMOvOZ4m2xcFZRLMwV8eu9H2kg5ZaDhK7DhzNufXuO-ToZqaWOHk6Ppg3y3Z_bezCV7dDL-XPMxy1ir8q4Mc1Xy2vVJ8F7oGfc68h1dlIqmVXsJUSysn4nApPkXdeVtR_9Phg8MNCZWlNNSxBSNqwIzvht3txXG-Brfl125UXMsoyRNgdE1OosphfzGaCiKH82wpKAzfAK1pbh8rwQBTRqJIKfARFcHOe4xn7Q0fXiFEW0CVIMYKY-d0s7oLvZ4vfJrw5oAPbw5OVmQOfjwt0oKT4Zl2z9VCeP6g017lk3hJUpDNFuoOw5cDE4ZaxfH", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-04-20T18:50:00.000Z", "utc_arrival": "2023-04-20T16:50:00.000Z", "local_departure": "2023-04-20T15:35:00.000Z", "utc_departure": "2023-04-20T13:35:00.000Z"}, {"id": "0b770a224c3000009c83bcac_0|0a220b774c33000096514b2c_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 744.117597, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 226192.9272, "conversion": {"EUR": 592.117977, "HUF": 226192.9272}, "fare": {"adults": 113096.46, "children": 113096.46, "infants": 113096.46}, "bags_price": {"1": 72.436, "2": 144.872}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 3}, "airlines": ["FR"], "route": [{"id": "0b770a224c3000009c83bcac_0", "combination_id": "0b770a224c3000009c83bcac", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-27T13:25:00.000Z", "utc_arrival": "2023-05-27T11:25:00.000Z", "local_departure": "2023-05-27T10:05:00.000Z", "utc_departure": "2023-05-27T08:05:00.000Z"}, {"id": "0a220b774c33000096514b2c_0", "combination_id": "0a220b774c33000096514b2c", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-30T14:05:00.000Z", "utc_arrival": "2023-05-30T12:05:00.000Z", "local_departure": "2023-05-30T10:55:00.000Z", "utc_departure": "2023-05-30T08:55:00.000Z"}], "booking_token": "EUt6PdWzWOLgaj9E9O3dqxeCLNkNTeClu_wvX5hP7FqpK3Mxcf2i2pBlO_7zzS7GSGldhJsAgim8FCsG2oLlxpXBKRbzVApKRpTns6td9ccEU4rXX7TOhMqklf-eL2ECic5TtcmD_aUw8LbuLR2stJMwSDJ_LOkmESSORE5msG_VpkSSBil-EfuuTu4f6ChinL7YkaVAQ-lDHuJQURaLKn0hNqOzWrT17eb3vW08QOqIBiVc-EsVKYWzBbdrmnNC19ADIXp63VQSTVg-P-pIQVSjnrReeGqywN6rltR8OWZrYcvCG8wB5peLLV9-qB59p9hFOl_XcdWC9d4K6Rfo-CFjllqK2Zf_e921Uzpw1mxdxIyyfHbG_rjKO3zmA_w_AkRCEwx3euJ2XEd3UiPKJs0U77X70xB_5O0L28XyQr0VueXQSNjReeDrcafrQNOActlpu6PeYW1HKBvcdA3XcW9X_A1Lg3zYcnmoHbpqt5iVkIjjJnY35PAbZ9QhDEnJu862EPYVBDp5533uwmIC-qLMwvrLv7Yg5n-vfSfZVZSFCEp-fKGnFprPdnZIxT7TTmxtYHINsp8kEWbEhl6A5nYJ0bfEnOGWUPJjiseOzJerasfSDJH_dMmF7RPRSppmZTI5k5OZw3z82Rz48hTkJ8EOZayK-1ooCpcX6QlwMWWMdydx_gIvSJZE0s_8HNtXhDwe5TFtu4CfH2WBdtHdZ-w==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c3000009c83bcac_0%7C0a220b774c33000096514b2c_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EUt6PdWzWOLgaj9E9O3dqxeCLNkNTeClu_wvX5hP7FqpK3Mxcf2i2pBlO_7zzS7GSGldhJsAgim8FCsG2oLlxpXBKRbzVApKRpTns6td9ccEU4rXX7TOhMqklf-eL2ECic5TtcmD_aUw8LbuLR2stJMwSDJ_LOkmESSORE5msG_VpkSSBil-EfuuTu4f6ChinL7YkaVAQ-lDHuJQURaLKn0hNqOzWrT17eb3vW08QOqIBiVc-EsVKYWzBbdrmnNC19ADIXp63VQSTVg-P-pIQVSjnrReeGqywN6rltR8OWZrYcvCG8wB5peLLV9-qB59p9hFOl_XcdWC9d4K6Rfo-CFjllqK2Zf_e921Uzpw1mxdxIyyfHbG_rjKO3zmA_w_AkRCEwx3euJ2XEd3UiPKJs0U77X70xB_5O0L28XyQr0VueXQSNjReeDrcafrQNOActlpu6PeYW1HKBvcdA3XcW9X_A1Lg3zYcnmoHbpqt5iVkIjjJnY35PAbZ9QhDEnJu862EPYVBDp5533uwmIC-qLMwvrLv7Yg5n-vfSfZVZSFCEp-fKGnFprPdnZIxT7TTmxtYHINsp8kEWbEhl6A5nYJ0bfEnOGWUPJjiseOzJerasfSDJH_dMmF7RPRSppmZTI5k5OZw3z82Rz48hTkJ8EOZayK-1ooCpcX6QlwMWWMdydx_gIvSJZE0s_8HNtXhDwe5TFtu4CfH2WBdtHdZ-w==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-27T13:25:00.000Z", "utc_arrival": "2023-05-27T11:25:00.000Z", "local_departure": "2023-05-27T10:05:00.000Z", "utc_departure": "2023-05-27T08:05:00.000Z"}, {"id": "0b770a224c2f0000d0b1f5bc_0|0a220b774c320000e133d3ca_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 744.381893, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 226293.89, "conversion": {"EUR": 592.382273, "HUF": 226293.89}, "fare": {"adults": 113146.95, "children": 113146.95, "infants": 113146.95}, "bags_price": {"1": 68.992, "2": 137.97}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 3}, "airlines": ["FR"], "route": [{"id": "0b770a224c2f0000d0b1f5bc_0", "combination_id": "0b770a224c2f0000d0b1f5bc", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-26T21:45:00.000Z", "utc_arrival": "2023-05-26T19:45:00.000Z", "local_departure": "2023-05-26T18:25:00.000Z", "utc_departure": "2023-05-26T16:25:00.000Z"}, {"id": "0a220b774c320000e133d3ca_0", "combination_id": "0a220b774c320000e133d3ca", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-29T10:15:00.000Z", "utc_arrival": "2023-05-29T08:15:00.000Z", "local_departure": "2023-05-29T07:05:00.000Z", "utc_departure": "2023-05-29T05:05:00.000Z"}], "booking_token": "EkD5BQJLcQqJAW4x9dBVd23QHsOs48rz1uUnYawsjtnOkiYhp_qZCoPaNmIpatO4csA_Ydobu7ZOwPh1qDGbIrIj8lCF3ffosVspYOFHMPlWoqLYCmZ7QXX61xdpUPL3ALW4IxN5Wi0L5PzJiTZWRZ58A2YYRZMQfy_J9SvaLNtVjhgp9OYrzjD8Z94rV7_YtI6fDzihlg8rGfiqk_CfcIdMvNnwriHc82ADVz-UDQm7tLWQvxPT52dlv8XvpoW3KV0hnD_RXlAxxu97jrXhISiq0Gjf6-zZgwwXPv8jENN-HELNvPlj6hdg0o2QmSuLW0cLvl3OWVi3k6XsQSAug16N1642jYWlZ5AUjQt2EeNNk348sAGx89Gh6uiPfrwfUgDuTy_8fajtE9m9yQZ8hu09JXYQHrYGo8uA3q7OmNrRpZs2NrkWNzHGUX5-_zh5V_HHu7olj3aBIwXo9mT8AEZUjouDA0K47AvECMIHxhj1u6xBmjHlbRLbFRM9agTOGxWI0Plt15BqQN4mxdvPfTtBdc1bYqWG8DjzZlElZvxpptB9uBpmlf0RVDD6IgCRkBNYyIu3bRLJs--a21VDEsDpDX83ATMU_uGVcV22DpvF2846O7Z2p_hsIwhdBHmbRpMOU91AtpP8a9ii9F79xs70BkatcvOjsO6VqT2xbogvoTuWh9g8QqCsWrz9_CXIp1J1FQQaVvZPFXdDxG-on6jwo_nEst0nvaPQkMY2I8sQ=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c2f0000d0b1f5bc_0%7C0a220b774c320000e133d3ca_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EkD5BQJLcQqJAW4x9dBVd23QHsOs48rz1uUnYawsjtnOkiYhp_qZCoPaNmIpatO4csA_Ydobu7ZOwPh1qDGbIrIj8lCF3ffosVspYOFHMPlWoqLYCmZ7QXX61xdpUPL3ALW4IxN5Wi0L5PzJiTZWRZ58A2YYRZMQfy_J9SvaLNtVjhgp9OYrzjD8Z94rV7_YtI6fDzihlg8rGfiqk_CfcIdMvNnwriHc82ADVz-UDQm7tLWQvxPT52dlv8XvpoW3KV0hnD_RXlAxxu97jrXhISiq0Gjf6-zZgwwXPv8jENN-HELNvPlj6hdg0o2QmSuLW0cLvl3OWVi3k6XsQSAug16N1642jYWlZ5AUjQt2EeNNk348sAGx89Gh6uiPfrwfUgDuTy_8fajtE9m9yQZ8hu09JXYQHrYGo8uA3q7OmNrRpZs2NrkWNzHGUX5-_zh5V_HHu7olj3aBIwXo9mT8AEZUjouDA0K47AvECMIHxhj1u6xBmjHlbRLbFRM9agTOGxWI0Plt15BqQN4mxdvPfTtBdc1bYqWG8DjzZlElZvxpptB9uBpmlf0RVDD6IgCRkBNYyIu3bRLJs--a21VDEsDpDX83ATMU_uGVcV22DpvF2846O7Z2p_hsIwhdBHmbRpMOU91AtpP8a9ii9F79xs70BkatcvOjsO6VqT2xbogvoTuWh9g8QqCsWrz9_CXIp1J1FQQaVvZPFXdDxG-on6jwo_nEst0nvaPQkMY2I8sQ=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-26T21:45:00.000Z", "utc_arrival": "2023-05-26T19:45:00.000Z", "local_departure": "2023-05-26T18:25:00.000Z", "utc_departure": "2023-05-26T16:25:00.000Z"}, {"id": "0b770a224c05000004bc72da_0|0a220b774c090000137a3e18_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 744.55573, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 226360.2969, "conversion": {"EUR": 592.55611, "HUF": 226360.2969}, "fare": {"adults": 113180.15, "children": 113180.15, "infants": 113180.15}, "bags_price": {"1": 83.006, "2": 166.012}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 6}, "airlines": ["FR"], "route": [{"id": "0b770a224c05000004bc72da_0", "combination_id": "0b770a224c05000004bc72da", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-14T21:45:00.000Z", "utc_arrival": "2023-04-14T19:45:00.000Z", "local_departure": "2023-04-14T18:25:00.000Z", "utc_departure": "2023-04-14T16:25:00.000Z"}, {"id": "0a220b774c090000137a3e18_0", "combination_id": "0a220b774c090000137a3e18", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-18T14:05:00.000Z", "utc_arrival": "2023-04-18T12:05:00.000Z", "local_departure": "2023-04-18T10:55:00.000Z", "utc_departure": "2023-04-18T08:55:00.000Z"}], "booking_token": "E-8ghrcG4MWxCYE5yCwbC4mVYlwpH55iQFhpD2AjC60GN8ieaS_QlZ1w78xuVQp4IJio1Y1VoY2q-0fgrNwlfDfqQOI1f0kqufJ5HoAn3oQn95rur2HGQIcKpht_ny19TsADyg9fYCm3efME1X68bXnyGkWlp6y-6EMAFhPwe8wWrakfgW-XOMegJLiSB3KTOvKr7RlqyIUtS2Ckik46PwYezpyYK6mVkIYvrhthGeUclymKvoj2n5x90fy2j6_eXyPjvNhi_thLfqtdDhEmAsKbpXgL4NzqDBQ_HQpehMoyQAiPdaFosalfo_ubam9sZ1itwm3u-1NsFlI6-MAWEwhlcnDCc_1j91wEmLi8p2DhdMDpbQ1jFuLAIbN2MIx-TUjQT-Cjlq-RT_DZERJCJdwY4lxs3qY0-eoDWtoc-4ulDThMGL-ZVsc1oycds5Ac9X8f_kPFlX0f-r5b9QEjHXHzzij75EC5iiq_VOpcgHRNsKPBy43HiJM_90ZwyCEF7tPqILr6aUpfTX0x0AB7t3nPkHAnZnexCo1Bym86AghRFHEj72jKeLpcIclljoI3rsj_TXd1XSz7-u2-al6TVu9A-ruUC8TTOKLleR0lr4TjFwBINylDMOqFa8CZvfrK6SkD_KeLcah4eISPZ7iIwTq5SBoL-ePkeA5Nf7KJ9PEgD20dGT9jiFJoKf1iIqXEZGRZnLbrz4QtK1OKQHT7hvA==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c05000004bc72da_0%7C0a220b774c090000137a3e18_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=E-8ghrcG4MWxCYE5yCwbC4mVYlwpH55iQFhpD2AjC60GN8ieaS_QlZ1w78xuVQp4IJio1Y1VoY2q-0fgrNwlfDfqQOI1f0kqufJ5HoAn3oQn95rur2HGQIcKpht_ny19TsADyg9fYCm3efME1X68bXnyGkWlp6y-6EMAFhPwe8wWrakfgW-XOMegJLiSB3KTOvKr7RlqyIUtS2Ckik46PwYezpyYK6mVkIYvrhthGeUclymKvoj2n5x90fy2j6_eXyPjvNhi_thLfqtdDhEmAsKbpXgL4NzqDBQ_HQpehMoyQAiPdaFosalfo_ubam9sZ1itwm3u-1NsFlI6-MAWEwhlcnDCc_1j91wEmLi8p2DhdMDpbQ1jFuLAIbN2MIx-TUjQT-Cjlq-RT_DZERJCJdwY4lxs3qY0-eoDWtoc-4ulDThMGL-ZVsc1oycds5Ac9X8f_kPFlX0f-r5b9QEjHXHzzij75EC5iiq_VOpcgHRNsKPBy43HiJM_90ZwyCEF7tPqILr6aUpfTX0x0AB7t3nPkHAnZnexCo1Bym86AghRFHEj72jKeLpcIclljoI3rsj_TXd1XSz7-u2-al6TVu9A-ruUC8TTOKLleR0lr4TjFwBINylDMOqFa8CZvfrK6SkD_KeLcah4eISPZ7iIwTq5SBoL-ePkeA5Nf7KJ9PEgD20dGT9jiFJoKf1iIqXEZGRZnLbrz4QtK1OKQHT7hvA==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-04-14T21:45:00.000Z", "utc_arrival": "2023-04-14T19:45:00.000Z", "local_departure": "2023-04-14T18:25:00.000Z", "utc_departure": "2023-04-14T16:25:00.000Z"}, {"id": "0b770a224c2e00002007cc72_0|0a220b774c310000cf80ab4c_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 745.212832, "distance": 1975.87, "duration": {"departure": 11700, "return": 11700, "total": 23400}, "price": 226611.3141, "conversion": {"EUR": 593.213212, "HUF": 226611.3141}, "fare": {"adults": 113305.66, "children": 113305.66, "infants": 113305.66}, "bags_price": {"1": 80.5, "2": 170.8}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 158, "hold_height": 52, "hold_length": 78, "hold_weight": 20, "hold_width": 28, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 3, "personal_item_width": 15}, "availability": {"seats": 4}, "airlines": ["W6", "VY"], "route": [{"id": "0b770a224c2e00002007cc72_0", "combination_id": "0b770a224c2e00002007cc72", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "VY", "flight_no": 5193, "operating_carrier": "IB", "operating_flight_no": "3279", "fare_basis": "WNBBLJA", "fare_category": "M", "fare_classes": "W", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-25T18:50:00.000Z", "utc_arrival": "2023-05-25T16:50:00.000Z", "local_departure": "2023-05-25T15:35:00.000Z", "utc_departure": "2023-05-25T13:35:00.000Z"}, {"id": "0a220b774c310000cf80ab4c_0", "combination_id": "0a220b774c310000cf80ab4c", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "JKREG", "fare_category": "M", "fare_classes": "J", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-28T21:05:00.000Z", "utc_arrival": "2023-05-28T19:05:00.000Z", "local_departure": "2023-05-28T17:50:00.000Z", "utc_departure": "2023-05-28T15:50:00.000Z"}], "booking_token": "EBjsbi5-UYHGIshy1znZp8ksjv1NEFSo9uPmCgyEFxI0LSjmfr-GQ27JfvJ00HSCxKT_uB3c3eWbs_hCyY1tbSH1rMf-dH1pBsJvykej84-G3JFNBJuwMDCuGBaN7T9AwDSNQgCUsfSel-SaChLelAskiFOWHmg01Bya0BznJNJr7KQO4almU6beCM005H2ojyqGiRasW5D8bbVfSKBa9oG-7UhXS38Ee9AL2es2mHBIZlpjK6aY4aRxHhc1wDiVT_r7LfDBrsAGICknDNWCh5KoAIjv6ef9xCZqqO5pUb1taNWvOJUwTcjVTa4TKtQ_QYTRGfVxLPUvMY8paLEaMIJhn0zsoLS_8M0zKdJqt7XXFK0hlM279yQH4c6fpCETV45T1e-pTGYRBLfzvBPrf5_eUij-T8TGpUb6zwoNxHoSDJCNOqliEKzesZcHgaRvxRVOonfTfXx1cCHzfGz0JPCVDKjpnABPW647MIJBmh-jDmd_bh89ToKGRTpx3CzGSJU1EcWgOPeRkuIZ8d66WVaatEhi9Eqa-AlXOnzDfKR1Xr516Yby9hp77NQ0NElhD8CtO162FY6acwhDZZjbwgtKWQsqiyhkzwRleUDKMBHAyEy1WhqNIszZ4Pc0t45bGwUeRxrY2mnSpcjGKfFyN32cE3zUbdwp10vBRwXGeZlDES4bkUNk55w5cB-1fAr9IBob3Tx77waSpinfEkIB1JE9oeqR0Z1oo8_6O2caKxQz7KFC2lDkIJgHuElMvOD6AkCe3uQUztGB1agjFSGnlNRT1PH4Fu0J_BwEV_fGAl-Y=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c2e00002007cc72_0%7C0a220b774c310000cf80ab4c_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EBjsbi5-UYHGIshy1znZp8ksjv1NEFSo9uPmCgyEFxI0LSjmfr-GQ27JfvJ00HSCxKT_uB3c3eWbs_hCyY1tbSH1rMf-dH1pBsJvykej84-G3JFNBJuwMDCuGBaN7T9AwDSNQgCUsfSel-SaChLelAskiFOWHmg01Bya0BznJNJr7KQO4almU6beCM005H2ojyqGiRasW5D8bbVfSKBa9oG-7UhXS38Ee9AL2es2mHBIZlpjK6aY4aRxHhc1wDiVT_r7LfDBrsAGICknDNWCh5KoAIjv6ef9xCZqqO5pUb1taNWvOJUwTcjVTa4TKtQ_QYTRGfVxLPUvMY8paLEaMIJhn0zsoLS_8M0zKdJqt7XXFK0hlM279yQH4c6fpCETV45T1e-pTGYRBLfzvBPrf5_eUij-T8TGpUb6zwoNxHoSDJCNOqliEKzesZcHgaRvxRVOonfTfXx1cCHzfGz0JPCVDKjpnABPW647MIJBmh-jDmd_bh89ToKGRTpx3CzGSJU1EcWgOPeRkuIZ8d66WVaatEhi9Eqa-AlXOnzDfKR1Xr516Yby9hp77NQ0NElhD8CtO162FY6acwhDZZjbwgtKWQsqiyhkzwRleUDKMBHAyEy1WhqNIszZ4Pc0t45bGwUeRxrY2mnSpcjGKfFyN32cE3zUbdwp10vBRwXGeZlDES4bkUNk55w5cB-1fAr9IBob3Tx77waSpinfEkIB1JE9oeqR0Z1oo8_6O2caKxQz7KFC2lDkIJgHuElMvOD6AkCe3uQUztGB1agjFSGnlNRT1PH4Fu0J_BwEV_fGAl-Y=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-25T18:50:00.000Z", "utc_arrival": "2023-05-25T16:50:00.000Z", "local_departure": "2023-05-25T15:35:00.000Z", "utc_departure": "2023-05-25T13:35:00.000Z"}, {"id": "0b770a224c270000783de5dc_0|0a220b774c2a0000038cbdad_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 749.508031, "distance": 1975.87, "duration": {"departure": 12600, "return": 11700, "total": 24300}, "price": 226724.0859, "conversion": {"EUR": 593.508421, "HUF": 226724.0859}, "fare": {"adults": 113362.04, "children": 113362.04, "infants": 113362.04}, "bags_price": {"1": 97.818, "2": 195.65}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 439, "hold_height": 149, "hold_length": 171, "hold_weight": 20, "hold_width": 119, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 2}, "airlines": ["W6"], "route": [{"id": "0b770a224c270000783de5dc_0", "combination_id": "0b770a224c270000783de5dc", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "JKREG", "fare_category": "M", "fare_classes": "J", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-18T21:15:00.000Z", "utc_arrival": "2023-05-18T19:15:00.000Z", "local_departure": "2023-05-18T17:45:00.000Z", "utc_departure": "2023-05-18T15:45:00.000Z"}, {"id": "0a220b774c2a0000038cbdad_0", "combination_id": "0a220b774c2a0000038cbdad", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "HREG", "fare_category": "M", "fare_classes": "H", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-21T21:05:00.000Z", "utc_arrival": "2023-05-21T19:05:00.000Z", "local_departure": "2023-05-21T17:50:00.000Z", "utc_departure": "2023-05-21T15:50:00.000Z"}], "booking_token": "EDYIXRUfZp7XXcu-7PSxcIaNEhy6cL2hUCmV7kTVhv8dM8kQ15TF0aDn3kcL5S6COY1JXpZZ9UeozT-7Q6jWSSvac3z71JhpIP_XYhJOkDsye-d37tRZPE2BM2JgsbHvLBMrtrxFLtVw1ladpbhoFDEOBUWTjLAq8MRF5z5ODiLKDhBSiE4uJTWpBTzdSwh_2MJF-Y06STq1AgmQC9o8L5iqsoWATYnPRMG5fsHfGTQB7sUO0dERrFezsJXv6LNoTfcy_KEcNQcz0R9611DXxAYCEW6RCcYsusupODttjX9IpqX3DkxuDOa8ZQ-JVS2QW5r2vGr-LaSpO1cMHNQ2ykh6rI0PYSEkfXaTNm1Df8CXFejMsXX7-D1S1guLJf20hzNUVkH48BqE0xHzxI6g_pyoSYRx1_FQdkI3Dp4q7aXXEWdVOVKrD9TJZAjW6G3Smk_u_4g6swZiSJ_6SKvuWyddFcFsWgu4WFrWGfWWsyBGtFeBerO2EaCS6cgWbrCtkl6yxb8L7oQSQ30dVhKeGtzQirsKBGHhae6NHGZNTssXQqRNZQCd8a-X108pv3fOzSVvqX0vKM8ktcfwc_tZGKPxZk-N7RN-opeby2sGRr-gsluqv8WOp6kOOCv5jGVP8AxFA4JIwSqAqYZ-bmG8FSPk3hdUAYlDLA7Tlve-9Mtch19YTYD9fgbIIXgRP8KVGAXTBolZAsZNSrOJSlVlvXqlPBxUbjL3kKThL3rdpkYE1sTZsDTndM26htaPfcUG2PPk7ZdmCrIFtAU7PWkI2vA==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c270000783de5dc_0%7C0a220b774c2a0000038cbdad_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EDYIXRUfZp7XXcu-7PSxcIaNEhy6cL2hUCmV7kTVhv8dM8kQ15TF0aDn3kcL5S6COY1JXpZZ9UeozT-7Q6jWSSvac3z71JhpIP_XYhJOkDsye-d37tRZPE2BM2JgsbHvLBMrtrxFLtVw1ladpbhoFDEOBUWTjLAq8MRF5z5ODiLKDhBSiE4uJTWpBTzdSwh_2MJF-Y06STq1AgmQC9o8L5iqsoWATYnPRMG5fsHfGTQB7sUO0dERrFezsJXv6LNoTfcy_KEcNQcz0R9611DXxAYCEW6RCcYsusupODttjX9IpqX3DkxuDOa8ZQ-JVS2QW5r2vGr-LaSpO1cMHNQ2ykh6rI0PYSEkfXaTNm1Df8CXFejMsXX7-D1S1guLJf20hzNUVkH48BqE0xHzxI6g_pyoSYRx1_FQdkI3Dp4q7aXXEWdVOVKrD9TJZAjW6G3Smk_u_4g6swZiSJ_6SKvuWyddFcFsWgu4WFrWGfWWsyBGtFeBerO2EaCS6cgWbrCtkl6yxb8L7oQSQ30dVhKeGtzQirsKBGHhae6NHGZNTssXQqRNZQCd8a-X108pv3fOzSVvqX0vKM8ktcfwc_tZGKPxZk-N7RN-opeby2sGRr-gsluqv8WOp6kOOCv5jGVP8AxFA4JIwSqAqYZ-bmG8FSPk3hdUAYlDLA7Tlve-9Mtch19YTYD9fgbIIXgRP8KVGAXTBolZAsZNSrOJSlVlvXqlPBxUbjL3kKThL3rdpkYE1sTZsDTndM26htaPfcUG2PPk7ZdmCrIFtAU7PWkI2vA==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-18T21:15:00.000Z", "utc_arrival": "2023-05-18T19:15:00.000Z", "local_departure": "2023-05-18T17:45:00.000Z", "utc_departure": "2023-05-18T15:45:00.000Z"}, {"id": "0b770a224c270000783de5dc_0|0a220b774c2b0000f0938698_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 749.508031, "distance": 1975.87, "duration": {"departure": 12600, "return": 11700, "total": 24300}, "price": 226724.0859, "conversion": {"EUR": 593.508421, "HUF": 226724.0859}, "fare": {"adults": 113362.04, "children": 113362.04, "infants": 113362.04}, "bags_price": {"1": 97.818, "2": 195.65}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 439, "hold_height": 149, "hold_length": 171, "hold_weight": 20, "hold_width": 119, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 2}, "airlines": ["W6"], "route": [{"id": "0b770a224c270000783de5dc_0", "combination_id": "0b770a224c270000783de5dc", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "JKREG", "fare_category": "M", "fare_classes": "J", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-18T21:15:00.000Z", "utc_arrival": "2023-05-18T19:15:00.000Z", "local_departure": "2023-05-18T17:45:00.000Z", "utc_departure": "2023-05-18T15:45:00.000Z"}, {"id": "0a220b774c2b0000f0938698_0", "combination_id": "0a220b774c2b0000f0938698", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "HREG", "fare_category": "M", "fare_classes": "H", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-22T23:45:00.000Z", "utc_arrival": "2023-05-22T21:45:00.000Z", "local_departure": "2023-05-22T20:30:00.000Z", "utc_departure": "2023-05-22T18:30:00.000Z"}], "booking_token": "EYtpbory9ptkZ9qbZZQf2Gu7stkSfLxN958CCeS8_-i2WTuRhGGETaMYS0i_2Z20ltmttLHcocEKFz0eKl0cXHI0FmUq2_dTEVS34rfiqYNytqYy7U-3NzqDN6n5GQN8S-34qLlsC99jf15nMUfRrpQwRACyHjyLXAf32iismjeE38LO7fEA8MUIDyfyQy2E6-9izmgc92G6hNEHu5wEesU3edPWgF_PiDrt0bUW8gDBCw--kBTUMFWXW3gQlIn0fNQyMxLNuyO_9nXXBZiRCs2jqLZHPITZz48Bv0qPzpE_6cinTHwkh3He93w65HJeKcemoH6MRqi_ScmYmVQWZQR53kHe7FMPaGRipKqC9MD7X8HAl0yxXvprngf7cVunpgJL4ORxCcKRcZDKS3vmktI8q5-Ud1HvZ7Zyp7a0ApVlxhcCE4NuGBWkl7wwmKAz_DUIdwrd_10gnwmbcELyR3gh5Z4L_RXr8WnwyMz2aYCG_beZaHPQLLrAC3sgbvOsNfW1wmcp9ksdiGICaT3kyASA9mJ6GGxcxJLyAKxPXi1rN_h-jhaVh6vZljmgwfjrCI2Qnu_j_FGmyj6x11DYlYDxN3fSR_5DFXs8ENqV3JxedZ92MAtUtgPEjieYyJG5yD2D52arDekrJwxtZelXwZ4KJ2U8Vkr6ogNDQdwOmshd18Q8SICphZbgVglp9bkwf1cQvAm4zr4ky2ZS1db2P7bCXqBf_M0afC0IX2xNtKWzPFuYQOHEfwki9ZS8l7iP8c5iA0W_M4THVapoh_DsrTA==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c270000783de5dc_0%7C0a220b774c2b0000f0938698_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EYtpbory9ptkZ9qbZZQf2Gu7stkSfLxN958CCeS8_-i2WTuRhGGETaMYS0i_2Z20ltmttLHcocEKFz0eKl0cXHI0FmUq2_dTEVS34rfiqYNytqYy7U-3NzqDN6n5GQN8S-34qLlsC99jf15nMUfRrpQwRACyHjyLXAf32iismjeE38LO7fEA8MUIDyfyQy2E6-9izmgc92G6hNEHu5wEesU3edPWgF_PiDrt0bUW8gDBCw--kBTUMFWXW3gQlIn0fNQyMxLNuyO_9nXXBZiRCs2jqLZHPITZz48Bv0qPzpE_6cinTHwkh3He93w65HJeKcemoH6MRqi_ScmYmVQWZQR53kHe7FMPaGRipKqC9MD7X8HAl0yxXvprngf7cVunpgJL4ORxCcKRcZDKS3vmktI8q5-Ud1HvZ7Zyp7a0ApVlxhcCE4NuGBWkl7wwmKAz_DUIdwrd_10gnwmbcELyR3gh5Z4L_RXr8WnwyMz2aYCG_beZaHPQLLrAC3sgbvOsNfW1wmcp9ksdiGICaT3kyASA9mJ6GGxcxJLyAKxPXi1rN_h-jhaVh6vZljmgwfjrCI2Qnu_j_FGmyj6x11DYlYDxN3fSR_5DFXs8ENqV3JxedZ92MAtUtgPEjieYyJG5yD2D52arDekrJwxtZelXwZ4KJ2U8Vkr6ogNDQdwOmshd18Q8SICphZbgVglp9bkwf1cQvAm4zr4ky2ZS1db2P7bCXqBf_M0afC0IX2xNtKWzPFuYQOHEfwki9ZS8l7iP8c5iA0W_M4THVapoh_DsrTA==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-18T21:15:00.000Z", "utc_arrival": "2023-05-18T19:15:00.000Z", "local_departure": "2023-05-18T17:45:00.000Z", "utc_departure": "2023-05-18T15:45:00.000Z"}, {"id": "0b770a224c2f0000c413678f_0|0a220b774c33000096514b2c_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 748.219904, "distance": 1975.87, "duration": {"departure": 12600, "return": 11400, "total": 24000}, "price": 226741.3537, "conversion": {"EUR": 593.553624, "HUF": 226741.3537}, "fare": {"adults": 113370.68, "children": 113370.68, "infants": 113370.68}, "bags_price": {"1": 92.022, "2": 184.044}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 2}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224c2f0000c413678f_0", "combination_id": "0b770a224c2f0000c413678f", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-26T19:45:00.000Z", "utc_arrival": "2023-05-26T17:45:00.000Z", "local_departure": "2023-05-26T16:15:00.000Z", "utc_departure": "2023-05-26T14:15:00.000Z"}, {"id": "0a220b774c33000096514b2c_0", "combination_id": "0a220b774c33000096514b2c", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-30T14:05:00.000Z", "utc_arrival": "2023-05-30T12:05:00.000Z", "local_departure": "2023-05-30T10:55:00.000Z", "utc_departure": "2023-05-30T08:55:00.000Z"}], "booking_token": "EpAKhymuIx6rt6H7c8T1vB6O1fPEvY0xOD9or0xT6-xcVbK0vUR2KEiFymNchbi2cHzPfqJBPUxsH8vB8rWsHA3NhPI-GE0dUi17tkIUgYJZaymUXiLUlDHqy5p1i-j_oEN6lZBw53eDFV28LJ2CpwsxyA3BZeT-r8AW5UsLUpqbVEgdNLYOxTc9B7grt4SUuZy9oiY4yyPvxTmDymDHAubTeo4QruO0DGlIE_69ne-DPA6rtDiIADLDJBK5uug6YKJ8oTrgYLBVllco6-AcNVp5tGYLlXFJFDMHSBHMNZ5N5VH3fok86zGHywQcSjr3G6BhA6oI7pHADugY2R0iqlZ_WEtFQ5pfkYlHd1a48oQc2I4x03UPGUGzU-NRmDBF-050PpquNdBpnw2n7L2voaPqA6Fy-HxEiU5aZoUNYcQffFFWsim6gIZ0pdLIyylkw3FKt2vzTRjOysquXupuTmC8YtR-6Og9d0DKniOPuoW7P4MAR3B1T4nsQkSwU0-FlvdjPqBhTujTI9G82bkGWwD3jpDBPxcDpZxf7GrzPL6sGvuMXAtDnegDEw6qixjTXbgu_-8sWurAHeRnziDXkWGFAoNjd0dO4U_slyRGJVlVnbqgJQro8BFLXGbm33CMef2dccvMWAndUEmItI2n1kKzcCzK7jC33crBIJ2b4H89KxGJDruBc6dcz1rOqhDSJtd7CdQGPvIly_GxjeUwUgCUvQZ5BNyz7NXRYXp8OaIzD_69R8FahBdPlUJ14ViE-ZaB6qryBUZzoz8yzVh2NNw==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c2f0000c413678f_0%7C0a220b774c33000096514b2c_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EpAKhymuIx6rt6H7c8T1vB6O1fPEvY0xOD9or0xT6-xcVbK0vUR2KEiFymNchbi2cHzPfqJBPUxsH8vB8rWsHA3NhPI-GE0dUi17tkIUgYJZaymUXiLUlDHqy5p1i-j_oEN6lZBw53eDFV28LJ2CpwsxyA3BZeT-r8AW5UsLUpqbVEgdNLYOxTc9B7grt4SUuZy9oiY4yyPvxTmDymDHAubTeo4QruO0DGlIE_69ne-DPA6rtDiIADLDJBK5uug6YKJ8oTrgYLBVllco6-AcNVp5tGYLlXFJFDMHSBHMNZ5N5VH3fok86zGHywQcSjr3G6BhA6oI7pHADugY2R0iqlZ_WEtFQ5pfkYlHd1a48oQc2I4x03UPGUGzU-NRmDBF-050PpquNdBpnw2n7L2voaPqA6Fy-HxEiU5aZoUNYcQffFFWsim6gIZ0pdLIyylkw3FKt2vzTRjOysquXupuTmC8YtR-6Og9d0DKniOPuoW7P4MAR3B1T4nsQkSwU0-FlvdjPqBhTujTI9G82bkGWwD3jpDBPxcDpZxf7GrzPL6sGvuMXAtDnegDEw6qixjTXbgu_-8sWurAHeRnziDXkWGFAoNjd0dO4U_slyRGJVlVnbqgJQro8BFLXGbm33CMef2dccvMWAndUEmItI2n1kKzcCzK7jC33crBIJ2b4H89KxGJDruBc6dcz1rOqhDSJtd7CdQGPvIly_GxjeUwUgCUvQZ5BNyz7NXRYXp8OaIzD_69R8FahBdPlUJ14ViE-ZaB6qryBUZzoz8yzVh2NNw==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-26T19:45:00.000Z", "utc_arrival": "2023-05-26T17:45:00.000Z", "local_departure": "2023-05-26T16:15:00.000Z", "utc_departure": "2023-05-26T14:15:00.000Z"}, {"id": "0b770a224c4000007558117a_0|0a220b774c430000391b6c3b_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 749.604509, "distance": 1975.87, "duration": {"departure": 12600, "return": 11700, "total": 24300}, "price": 226760.9411, "conversion": {"EUR": 593.604899, "HUF": 226760.9411}, "fare": {"adults": 113380.47, "children": 113380.47, "infants": 113380.47}, "bags_price": {"1": 121.814, "2": 243.642}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 439, "hold_height": 149, "hold_length": 171, "hold_weight": 20, "hold_width": 119, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 3}, "airlines": ["W6"], "route": [{"id": "0b770a224c4000007558117a_0", "combination_id": "0b770a224c4000007558117a", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "HREG", "fare_category": "M", "fare_classes": "H", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-12T19:45:00.000Z", "utc_arrival": "2023-06-12T17:45:00.000Z", "local_departure": "2023-06-12T16:15:00.000Z", "utc_departure": "2023-06-12T14:15:00.000Z"}, {"id": "0a220b774c430000391b6c3b_0", "combination_id": "0a220b774c430000391b6c3b", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "JREG", "fare_category": "M", "fare_classes": "J", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-16T01:15:00.000Z", "utc_arrival": "2023-06-15T23:15:00.000Z", "local_departure": "2023-06-15T22:00:00.000Z", "utc_departure": "2023-06-15T20:00:00.000Z"}], "booking_token": "ECfoORgJpU4CRHM26JDeHYx0yULdjQF1qaEIIte03VuAMPruhUzHdqlY1SPIovQWSjGZIPJ1-2fpCYK24HOfxaJb4ASpikyOxuMaKPKH9bvTtHiyu04uv03u1aD1XzTBAlki_QBmCk9bzkexUaUas4oX9u6cag_wt6rCbzTkf4FTTGo3E0nT-BKXH7VNL2D5xtvU_px84inzpWoh0tg9y7kFcOT9iEjmU6I9cnj0_jxk1f5G3afnrd3BeoWA0A2Asauizvx9bvMvw7ov2rxqYkY7_3DAya_doGZS9L1vzgrvOqeb99vu-qsxfac-6EP8MGWn_qp6GcsJ4ZhM07wWIoDedz3tTwFqhpSt0fQxDBl7sETR3n2WcBPg8gEBMbMpr2Kfw8ikcbHxvB1tCGDGLeFWXjYANO4aKfUE9iH_L37wS-nvNIaUxVkRhVuzHU8xskUfTvnn2hNGWbfMLeTO1-SNC1ebjoUPSXx2bo6w40-B7DX7g_QLQcosDlnYwmb2D2ZhOMKFMih40vWzua9-ivvZTxdA_19XYlYCmNNWsZ1Hu4RgP1Gg5D8CwH9ZLUIF8B76crNnH4diNq9vBTRSt-28HUyG0jd3-erIiDuB4DbeA3xhwct3AXRzD6YIdK30JXjoZ7O9zsMikDxaX-OyGY6Udc6zfkO8-SaWQJxK9-R7R8QVu-417_yUxTKq_ACnX6ATnpkeAFjIQpyzD1isvdD-jeUKYQm2VVjvSJnVc5sR0IBOirhy2gkMzc_9zG4tPa7S4Dvi5lh0MJUA7Go0mXlwleDimP5GtcWHnrfSzM7o=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c4000007558117a_0%7C0a220b774c430000391b6c3b_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=ECfoORgJpU4CRHM26JDeHYx0yULdjQF1qaEIIte03VuAMPruhUzHdqlY1SPIovQWSjGZIPJ1-2fpCYK24HOfxaJb4ASpikyOxuMaKPKH9bvTtHiyu04uv03u1aD1XzTBAlki_QBmCk9bzkexUaUas4oX9u6cag_wt6rCbzTkf4FTTGo3E0nT-BKXH7VNL2D5xtvU_px84inzpWoh0tg9y7kFcOT9iEjmU6I9cnj0_jxk1f5G3afnrd3BeoWA0A2Asauizvx9bvMvw7ov2rxqYkY7_3DAya_doGZS9L1vzgrvOqeb99vu-qsxfac-6EP8MGWn_qp6GcsJ4ZhM07wWIoDedz3tTwFqhpSt0fQxDBl7sETR3n2WcBPg8gEBMbMpr2Kfw8ikcbHxvB1tCGDGLeFWXjYANO4aKfUE9iH_L37wS-nvNIaUxVkRhVuzHU8xskUfTvnn2hNGWbfMLeTO1-SNC1ebjoUPSXx2bo6w40-B7DX7g_QLQcosDlnYwmb2D2ZhOMKFMih40vWzua9-ivvZTxdA_19XYlYCmNNWsZ1Hu4RgP1Gg5D8CwH9ZLUIF8B76crNnH4diNq9vBTRSt-28HUyG0jd3-erIiDuB4DbeA3xhwct3AXRzD6YIdK30JXjoZ7O9zsMikDxaX-OyGY6Udc6zfkO8-SaWQJxK9-R7R8QVu-417_yUxTKq_ACnX6ATnpkeAFjIQpyzD1isvdD-jeUKYQm2VVjvSJnVc5sR0IBOirhy2gkMzc_9zG4tPa7S4Dvi5lh0MJUA7Go0mXlwleDimP5GtcWHnrfSzM7o=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-12T19:45:00.000Z", "utc_arrival": "2023-06-12T17:45:00.000Z", "local_departure": "2023-06-12T16:15:00.000Z", "utc_departure": "2023-06-12T14:15:00.000Z"}, {"id": "0b770a224c16000010748fcb_0|0a220b774c1a0000983284f5_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 748.407416, "distance": 1975.87, "duration": {"departure": 12600, "return": 11400, "total": 24000}, "price": 226812.9846, "conversion": {"EUR": 593.741136, "HUF": 226812.9846}, "fare": {"adults": 113406.49, "children": 113406.49, "infants": 113406.49}, "bags_price": {"1": 96.6, "2": 193.214}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 2}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224c16000010748fcb_0", "combination_id": "0b770a224c16000010748fcb", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "JKREG", "fare_category": "M", "fare_classes": "J", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-01T19:45:00.000Z", "utc_arrival": "2023-05-01T17:45:00.000Z", "local_departure": "2023-05-01T16:15:00.000Z", "utc_departure": "2023-05-01T14:15:00.000Z"}, {"id": "0a220b774c1a0000983284f5_0", "combination_id": "0a220b774c1a0000983284f5", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-05T18:00:00.000Z", "utc_arrival": "2023-05-05T16:00:00.000Z", "local_departure": "2023-05-05T14:50:00.000Z", "utc_departure": "2023-05-05T12:50:00.000Z"}], "booking_token": "EXMZpVZ0M4u11rVV9vEqzIpgffezcocogm7kSQHjVyrOkj5TFIAn0t3jRpF_yrTFuKrKPejQhKMQaDx4xJKBF6yeZNQM3N64BJUwh4xEmSEWasRFV4acG6Is-GkrcJPIi14-7saLsDxmEWWadhgsStLVOVHhI-nCkW7r5FBwrqzXq1RsRCJZ1C76ixWfljoJLNOeD8FGwHxRqm6HNvPWlZxed_l43UZZFSpAwXIMjjvCvZ3R2CDI1K63_6670WoSWP4jH2xtF7OIcPvwy5bo1629RKCxtwqxuAjZsQmMdrv35XE_8ENjUyfQPN1bWB3c60wAj_W2L2ez4x1iYyGFeYzf5BnsXL2uBRybpdPC5V9ER0W0s7UKDyZDYgYmCzDVZR6E_cEVizCiuKMOMyP1nk_g0q4PIdZlYsYBYgEEgjZiC7hoTXSW9Y6m6SD5OwGTaXEjoCAGn7OIXj4zye1DdALUNbCz_BtExUuCiurboKj0CX90atdUNV3EbDEc41U26PYmRWWtH3uougPZqEbI4dfs0QlHpvk3gv5sJswoWDt5Po2MBiPLlUL_QtHJbqOHSGy2MK_hYLXHENgO9Qlx1lsvMr1E_59fnfGhe2y2-4QJXI3NYkojHLolIbcJXtE-hWILd6Chn3kdI5moLlD9SF6WFlZ6I9fgAirjmq8RK6MzcE7kHd51fMVgnccdLe8Hjqvo6ot-ZesT5dl8f05B79DyjLWRwkE46-6zv_YqZ443FZXN_9LOKz8OAYJc78u6SMc-q4Qbv6o9zQtLjYX_JmQ==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c16000010748fcb_0%7C0a220b774c1a0000983284f5_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EXMZpVZ0M4u11rVV9vEqzIpgffezcocogm7kSQHjVyrOkj5TFIAn0t3jRpF_yrTFuKrKPejQhKMQaDx4xJKBF6yeZNQM3N64BJUwh4xEmSEWasRFV4acG6Is-GkrcJPIi14-7saLsDxmEWWadhgsStLVOVHhI-nCkW7r5FBwrqzXq1RsRCJZ1C76ixWfljoJLNOeD8FGwHxRqm6HNvPWlZxed_l43UZZFSpAwXIMjjvCvZ3R2CDI1K63_6670WoSWP4jH2xtF7OIcPvwy5bo1629RKCxtwqxuAjZsQmMdrv35XE_8ENjUyfQPN1bWB3c60wAj_W2L2ez4x1iYyGFeYzf5BnsXL2uBRybpdPC5V9ER0W0s7UKDyZDYgYmCzDVZR6E_cEVizCiuKMOMyP1nk_g0q4PIdZlYsYBYgEEgjZiC7hoTXSW9Y6m6SD5OwGTaXEjoCAGn7OIXj4zye1DdALUNbCz_BtExUuCiurboKj0CX90atdUNV3EbDEc41U26PYmRWWtH3uougPZqEbI4dfs0QlHpvk3gv5sJswoWDt5Po2MBiPLlUL_QtHJbqOHSGy2MK_hYLXHENgO9Qlx1lsvMr1E_59fnfGhe2y2-4QJXI3NYkojHLolIbcJXtE-hWILd6Chn3kdI5moLlD9SF6WFlZ6I9fgAirjmq8RK6MzcE7kHd51fMVgnccdLe8Hjqvo6ot-ZesT5dl8f05B79DyjLWRwkE46-6zv_YqZ443FZXN_9LOKz8OAYJc78u6SMc-q4Qbv6o9zQtLjYX_JmQ==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-01T19:45:00.000Z", "utc_arrival": "2023-05-01T17:45:00.000Z", "local_departure": "2023-05-01T16:15:00.000Z", "utc_departure": "2023-05-01T14:15:00.000Z"}, {"id": "0b770a224bf1000079e32495_0|0a220b774bf400002dbcb9a5_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 747.862127, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 227623.3621, "conversion": {"EUR": 595.862507, "HUF": 227623.3621}, "fare": {"adults": 113811.68, "children": 113811.68, "infants": 113811.68}, "bags_price": {"1": 86.24, "2": 172.494}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 6}, "airlines": ["FR"], "route": [{"id": "0b770a224bf1000079e32495_0", "combination_id": "0b770a224bf1000079e32495", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-03-25T21:50:00.000Z", "utc_arrival": "2023-03-25T20:50:00.000Z", "local_departure": "2023-03-25T18:30:00.000Z", "utc_departure": "2023-03-25T17:30:00.000Z"}, {"id": "0a220b774bf400002dbcb9a5_0", "combination_id": "0a220b774bf400002dbcb9a5", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-03-28T14:05:00.000Z", "utc_arrival": "2023-03-28T12:05:00.000Z", "local_departure": "2023-03-28T10:55:00.000Z", "utc_departure": "2023-03-28T08:55:00.000Z"}], "booking_token": "ElLLScaTNcNjlnUgkLGMJKiagvoJBuFCRNo4z9UdOvmzWxaF2vdhp4EydwTy20VVLGGKJUcZf2xMQlbeFqWo46LmV-xu_qYj-I6Nc9-trRXva2bqVavMc2XMOMw4ABHfYkm3H0BKGDEX4JyQ14PX2ZiiHDaVFFN1rjXiVg4slL84YsUi1vK2s-v8Ha7v0LKTCvK4NA_POc8c-7lz6KvLKejLRD6ooo597Yhz7Qra2hchKF8oPHk_GCngjWR9g0sP5iSbxlonlQ13lXysZnT98zv--oM977E-W4IvHb0TbRcgP2Kr92fABXPbElDqmMV4LhZo4hXcBMseEpqpOyv75n2Of4icLfBVZsHcl9NLA-i5oheTRtZvsCeA8gQ4nxGT8_UrkcmJ_n3GZkh5sXTkr5zNb5OHDm6ia4hqCrROD7fO3waMkpdx7WuMa03b675G332N9Z-r8r5WJ519VUlD3N3TtWssBCKSgy_NBpY6O0fuBwDW8qQCVbrnmjRvQMGp8AtQj0WO1bSi-iUMA295gpwrI0yDFON6LXnXwgmBGOTYSE3o4zc7XAs74d8lpnQtTdvbDw0sxDah4N9ENWL7aChjuMZG6bOQrSe1GcFm9FjXZ_L-sm7gs9bPdM4EfwfAVhMtpOk3k3laoTf2bHRyjsS3W5jZ_xdXJYqvBjQ_9I7OIeVgibijh1-ieaNiA7JiThfoPdsYIDAPSwBwzajDwjLQzlxklDv0O3tWDVtNYj_g=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224bf1000079e32495_0%7C0a220b774bf400002dbcb9a5_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=ElLLScaTNcNjlnUgkLGMJKiagvoJBuFCRNo4z9UdOvmzWxaF2vdhp4EydwTy20VVLGGKJUcZf2xMQlbeFqWo46LmV-xu_qYj-I6Nc9-trRXva2bqVavMc2XMOMw4ABHfYkm3H0BKGDEX4JyQ14PX2ZiiHDaVFFN1rjXiVg4slL84YsUi1vK2s-v8Ha7v0LKTCvK4NA_POc8c-7lz6KvLKejLRD6ooo597Yhz7Qra2hchKF8oPHk_GCngjWR9g0sP5iSbxlonlQ13lXysZnT98zv--oM977E-W4IvHb0TbRcgP2Kr92fABXPbElDqmMV4LhZo4hXcBMseEpqpOyv75n2Of4icLfBVZsHcl9NLA-i5oheTRtZvsCeA8gQ4nxGT8_UrkcmJ_n3GZkh5sXTkr5zNb5OHDm6ia4hqCrROD7fO3waMkpdx7WuMa03b675G332N9Z-r8r5WJ519VUlD3N3TtWssBCKSgy_NBpY6O0fuBwDW8qQCVbrnmjRvQMGp8AtQj0WO1bSi-iUMA295gpwrI0yDFON6LXnXwgmBGOTYSE3o4zc7XAs74d8lpnQtTdvbDw0sxDah4N9ENWL7aChjuMZG6bOQrSe1GcFm9FjXZ_L-sm7gs9bPdM4EfwfAVhMtpOk3k3laoTf2bHRyjsS3W5jZ_xdXJYqvBjQ_9I7OIeVgibijh1-ieaNiA7JiThfoPdsYIDAPSwBwzajDwjLQzlxklDv0O3tWDVtNYj_g=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-03-25T21:50:00.000Z", "utc_arrival": "2023-03-25T20:50:00.000Z", "local_departure": "2023-03-25T18:30:00.000Z", "utc_departure": "2023-03-25T17:30:00.000Z"}, {"id": "0b770a224bec0000d03c291b_0|0a220b774bef00006f39da1f_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 749.788432, "distance": 1975.87, "duration": {"departure": 12000, "return": 11700, "total": 23700}, "price": 227849.8824, "conversion": {"EUR": 596.455482, "HUF": 227849.8824}, "fare": {"adults": 113924.94, "children": 113924.94, "infants": 113924.94}, "bags_price": {"1": 97.622, "2": 195.258}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 439, "hold_height": 149, "hold_length": 171, "hold_weight": 20, "hold_width": 119, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 3}, "airlines": ["W6"], "route": [{"id": "0b770a224bec0000d03c291b_0", "combination_id": "0b770a224bec0000d03c291b", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IJREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-03-20T08:20:00.000Z", "utc_arrival": "2023-03-20T07:20:00.000Z", "local_departure": "2023-03-20T05:00:00.000Z", "utc_departure": "2023-03-20T04:00:00.000Z"}, {"id": "0a220b774bef00006f39da1f_0", "combination_id": "0a220b774bef00006f39da1f", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-03-24T00:05:00.000Z", "utc_arrival": "2023-03-23T23:05:00.000Z", "local_departure": "2023-03-23T20:50:00.000Z", "utc_departure": "2023-03-23T19:50:00.000Z"}], "booking_token": "Eca6-Ym0CWM9ZM8eEYGs-5qsbEEOEIJbxCu_VoRQBrQpiOlQFbRbGChHWDhD1qPOT2btGuO-z3DqfcgqNbGYGUXNK4D-g2PPdwQbed1pMs4ed4F_FNZq24-Qt68Q4bTw5HAH5JUfrO-3bADPwOp-L63BTbHu0RRLoDwPQiu_yavlRkUlImNn8EG3VP-1T5LRPR6V2uypZzk75rgyWnMpmk_tFx7LizhjhflMKoI-CzBFxn28PKYdhDjFba8eBecSrSgcB17-e4YDHuDKGNZVo_xprl_CMNi93Ht53fM-R1spwSWn8rrv9tlZHLHldKNfLygDkJZX8xehDDWykB4wCJx4DHo_nQRs2HXggEKhw5UqEE6yCAkPw0mVADDn7dZjUkzSjXHdJdOLQvTDVDdsJudHJd9vKgFy6M2hdRlu1UOke7SPNxT786zYB1ED-WLo2pIH86txAksf8vtg5QKg0G6_xo5wwHlm0G1rDub1Peb3JcwJc86oSxWx-UI2P27EHqd4aimWLpEgQcsQkbG58LvSv-m2BJa8Qvzd-C645ummM4v_7h8k4mbELRmgQdlvb2gbBcgLteYHEirWeBzRn_hHA_a51Txg-M42TLqogCscIZtV_UmOUzuX9Kp2Wvhs5gG-S3w2cdMlukx_wdSYz4gok-wd0ajyjhpO0uVgJiqNIfYbcaqY8UPO3RiT5zx1-5K86n1R5FV7ftf4U3ovti8Bma8nSZatD8oM6rrWV6FHVRyej0JSNWzlRxuZSKSdKbxd5pKGWVE7MqYeYEI0HQg==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224bec0000d03c291b_0%7C0a220b774bef00006f39da1f_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=Eca6-Ym0CWM9ZM8eEYGs-5qsbEEOEIJbxCu_VoRQBrQpiOlQFbRbGChHWDhD1qPOT2btGuO-z3DqfcgqNbGYGUXNK4D-g2PPdwQbed1pMs4ed4F_FNZq24-Qt68Q4bTw5HAH5JUfrO-3bADPwOp-L63BTbHu0RRLoDwPQiu_yavlRkUlImNn8EG3VP-1T5LRPR6V2uypZzk75rgyWnMpmk_tFx7LizhjhflMKoI-CzBFxn28PKYdhDjFba8eBecSrSgcB17-e4YDHuDKGNZVo_xprl_CMNi93Ht53fM-R1spwSWn8rrv9tlZHLHldKNfLygDkJZX8xehDDWykB4wCJx4DHo_nQRs2HXggEKhw5UqEE6yCAkPw0mVADDn7dZjUkzSjXHdJdOLQvTDVDdsJudHJd9vKgFy6M2hdRlu1UOke7SPNxT786zYB1ED-WLo2pIH86txAksf8vtg5QKg0G6_xo5wwHlm0G1rDub1Peb3JcwJc86oSxWx-UI2P27EHqd4aimWLpEgQcsQkbG58LvSv-m2BJa8Qvzd-C645ummM4v_7h8k4mbELRmgQdlvb2gbBcgLteYHEirWeBzRn_hHA_a51Txg-M42TLqogCscIZtV_UmOUzuX9Kp2Wvhs5gG-S3w2cdMlukx_wdSYz4gok-wd0ajyjhpO0uVgJiqNIfYbcaqY8UPO3RiT5zx1-5K86n1R5FV7ftf4U3ovti8Bma8nSZatD8oM6rrWV6FHVRyej0JSNWzlRxuZSKSdKbxd5pKGWVE7MqYeYEI0HQg==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-03-20T08:20:00.000Z", "utc_arrival": "2023-03-20T07:20:00.000Z", "local_departure": "2023-03-20T05:00:00.000Z", "utc_departure": "2023-03-20T04:00:00.000Z"}, {"id": "0b770a224c32000091ac2e03_0|0a220b774c35000063a8527d_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 751.065776, "distance": 1975.87, "duration": {"departure": 12000, "return": 11700, "total": 23700}, "price": 228337.8362, "conversion": {"EUR": 597.732826, "HUF": 228337.8362}, "fare": {"adults": 114168.92, "children": 114168.92, "infants": 114168.92}, "bags_price": {"1": 88.396, "2": 176.792}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 4}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224c32000091ac2e03_0", "combination_id": "0b770a224c32000091ac2e03", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-29T14:00:00.000Z", "utc_arrival": "2023-05-29T12:00:00.000Z", "local_departure": "2023-05-29T10:40:00.000Z", "utc_departure": "2023-05-29T08:40:00.000Z"}, {"id": "0a220b774c35000063a8527d_0", "combination_id": "0a220b774c35000063a8527d", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "HIREG", "fare_category": "M", "fare_classes": "H", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-02T01:15:00.000Z", "utc_arrival": "2023-06-01T23:15:00.000Z", "local_departure": "2023-06-01T22:00:00.000Z", "utc_departure": "2023-06-01T20:00:00.000Z"}], "booking_token": "E7moMy3ctRxQ6NhOeubTrGMpsmn_GK_GKfvgIfmOyvEd0NXyFgs2UgI4zcvRF_3uZbu5GMJkxP1URnjm2-XbmwVKSCdzoiyGwbZGUnbFLXNGTNMVy69FjAdGxsv99tWPeAn30PBbISBK17YHCxIfwb3Biy8DJmJRf3QBWMbsDLLXcvLuNgl3gkdZtexRg9kY-qTEIa3sZuRMeFtKWHrSRif63_MziA3onxrIqm7HYCTyAG_y5-rkkopzvkg0SjwaSrG30A1ErljodjnkYbiXUthnzYCyGqKe9J5jJzHeeJkO1z7xsSaW6YPrjz0B8YplUMvHnPvlZmuj0PoujqSP2joeue3MY2BQEH9Kxs3emBwoLAULGrY8WC6OLguxn64cco3IH00CjdTs0f4PKRO6cMazquIJ6iL5i-7SzZpL__Cr06YjH_owHWPVZUyDydKvq3gdXddl31U0KQ0JaF6SxkzK42NVTZgIB6N7J8pQCU5RI8IcZziDMDPxQvjltCbY-D_idJeiIphV8D8AtrecUSrFL38FiAX7m2ZelZfnpmTBoJjHC2aI9ZEyLrzF3-BPWiBzurdwQHYsTDpi9B-282uMLpOapE5LgnCD37aO3HD2HH_GTy2Fv2zGHNg-k5l29QV1yr4ArZmC38H6WADk9KpnrQeIcm--UTcmOKymj3dU3vr8ugj7Bw9jYTQyrm1TmFkYpwJMZ5J78fQ-6Bf7EqoXxHOn-F0j0C3SovKof4QKfxhau14naaqg7OS_4E3q5f2nnEuEkyYDYUP1zjHOMNw==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c32000091ac2e03_0%7C0a220b774c35000063a8527d_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=E7moMy3ctRxQ6NhOeubTrGMpsmn_GK_GKfvgIfmOyvEd0NXyFgs2UgI4zcvRF_3uZbu5GMJkxP1URnjm2-XbmwVKSCdzoiyGwbZGUnbFLXNGTNMVy69FjAdGxsv99tWPeAn30PBbISBK17YHCxIfwb3Biy8DJmJRf3QBWMbsDLLXcvLuNgl3gkdZtexRg9kY-qTEIa3sZuRMeFtKWHrSRif63_MziA3onxrIqm7HYCTyAG_y5-rkkopzvkg0SjwaSrG30A1ErljodjnkYbiXUthnzYCyGqKe9J5jJzHeeJkO1z7xsSaW6YPrjz0B8YplUMvHnPvlZmuj0PoujqSP2joeue3MY2BQEH9Kxs3emBwoLAULGrY8WC6OLguxn64cco3IH00CjdTs0f4PKRO6cMazquIJ6iL5i-7SzZpL__Cr06YjH_owHWPVZUyDydKvq3gdXddl31U0KQ0JaF6SxkzK42NVTZgIB6N7J8pQCU5RI8IcZziDMDPxQvjltCbY-D_idJeiIphV8D8AtrecUSrFL38FiAX7m2ZelZfnpmTBoJjHC2aI9ZEyLrzF3-BPWiBzurdwQHYsTDpi9B-282uMLpOapE5LgnCD37aO3HD2HH_GTy2Fv2zGHNg-k5l29QV1yr4ArZmC38H6WADk9KpnrQeIcm--UTcmOKymj3dU3vr8ugj7Bw9jYTQyrm1TmFkYpwJMZ5J78fQ-6Bf7EqoXxHOn-F0j0C3SovKof4QKfxhau14naaqg7OS_4E3q5f2nnEuEkyYDYUP1zjHOMNw==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-29T14:00:00.000Z", "utc_arrival": "2023-05-29T12:00:00.000Z", "local_departure": "2023-05-29T10:40:00.000Z", "utc_departure": "2023-05-29T08:40:00.000Z"}, {"id": "0b770a224c0800005e1413f9_0|0a220b774c0c0000c53091b6_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 759.067807, "distance": 1975.87, "duration": {"departure": 12600, "return": 12900, "total": 25500}, "price": 228338.6196, "conversion": {"EUR": 597.734877, "HUF": 228338.6196}, "fare": {"adults": 114169.31, "children": 118067.74, "infants": 118067.74}, "bags_price": {"1": 119.224, "2": 238.434}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 439, "hold_height": 149, "hold_length": 171, "hold_weight": 20, "hold_width": 119, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 3}, "airlines": ["W6"], "route": [{"id": "0b770a224c0800005e1413f9_0", "combination_id": "0b770a224c0800005e1413f9", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "JREG", "fare_category": "M", "fare_classes": "J", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-17T19:45:00.000Z", "utc_arrival": "2023-04-17T17:45:00.000Z", "local_departure": "2023-04-17T16:15:00.000Z", "utc_departure": "2023-04-17T14:15:00.000Z"}, {"id": "0a220b774c0c0000c53091b6_0", "combination_id": "0a220b774c0c0000c53091b6", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IJREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-22T00:05:00.000Z", "utc_arrival": "2023-04-21T22:05:00.000Z", "local_departure": "2023-04-21T20:30:00.000Z", "utc_departure": "2023-04-21T18:30:00.000Z"}], "booking_token": "EdIls0dp3qxKShbjJxJO4Em6e3GRQSXrcudgjrz2p_-Mg7H_K2eqgDpyiUninp4FQoYQTgbTuTsEPEEe-fqAjzfhVcI41C_nCFQWmSwX0KBgf0b43RQ7Va732196r4TPeCr9a4Qo5UR--gcUQOxvtHCh9WtICb211jHOxRpcdxGa6goB3G6u4-9F5EX5s2OcyTP4mOM_0bXh-DTz5WK4ekcyEi6pvQTl9s4bvBfyfIhxwbEDs8HlgHKcG6vc7ow5NIFlUMZha1ceaRX7cRftkjovCfLngTDQmZU9eu2yzpZ2WH5MH_aPx9IWIIOLu8RC2gN8RrMxZtGwJBDKdzQApv-LE8wxgx7nu5d9lzEQFZuVLExFNs6wx9q1QANJvzhDKU2bs5Ah2et0dv4gePnfpoBxBEP8l3usW5pD1nb9adCnZ6ZufHtPsX73IMvI9QFWjGripV8870kXA2WCFO5szWTlyKt0mP7I7NVE2KKzNHZRL3_-5nfED41v3HzkXE_ImRqfUuGq9ijFyFz8s52leAHf4g9YSZ4ySf3cQDkQsKluWYPEaglKx9zhAcIGv1lq74y_dCBlQq1E8RFP6w5X48w3dpEjmhtJ3pdI1aIXyOBEY2GrP7BnYj9_UdWgQD_UaTdT-QWI4Yy9VtypWHz8bk0udaGz07xRJRR4TdzOXuxC6fgDg3Ecg6_LVaRt-sG11QMJuVVRL1ky_2TTDWgnUpx5nS2bm-8Dar7gnBOD7MGxmuDUaQFIzfIqJ0DxUHTJdg1JctIIiU5PONHWp0Pq4f7z8qg_RH20Y3wjCSihk9Do=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c0800005e1413f9_0%7C0a220b774c0c0000c53091b6_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EdIls0dp3qxKShbjJxJO4Em6e3GRQSXrcudgjrz2p_-Mg7H_K2eqgDpyiUninp4FQoYQTgbTuTsEPEEe-fqAjzfhVcI41C_nCFQWmSwX0KBgf0b43RQ7Va732196r4TPeCr9a4Qo5UR--gcUQOxvtHCh9WtICb211jHOxRpcdxGa6goB3G6u4-9F5EX5s2OcyTP4mOM_0bXh-DTz5WK4ekcyEi6pvQTl9s4bvBfyfIhxwbEDs8HlgHKcG6vc7ow5NIFlUMZha1ceaRX7cRftkjovCfLngTDQmZU9eu2yzpZ2WH5MH_aPx9IWIIOLu8RC2gN8RrMxZtGwJBDKdzQApv-LE8wxgx7nu5d9lzEQFZuVLExFNs6wx9q1QANJvzhDKU2bs5Ah2et0dv4gePnfpoBxBEP8l3usW5pD1nb9adCnZ6ZufHtPsX73IMvI9QFWjGripV8870kXA2WCFO5szWTlyKt0mP7I7NVE2KKzNHZRL3_-5nfED41v3HzkXE_ImRqfUuGq9ijFyFz8s52leAHf4g9YSZ4ySf3cQDkQsKluWYPEaglKx9zhAcIGv1lq74y_dCBlQq1E8RFP6w5X48w3dpEjmhtJ3pdI1aIXyOBEY2GrP7BnYj9_UdWgQD_UaTdT-QWI4Yy9VtypWHz8bk0udaGz07xRJRR4TdzOXuxC6fgDg3Ecg6_LVaRt-sG11QMJuVVRL1ky_2TTDWgnUpx5nS2bm-8Dar7gnBOD7MGxmuDUaQFIzfIqJ0DxUHTJdg1JctIIiU5PONHWp0Pq4f7z8qg_RH20Y3wjCSihk9Do=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-04-17T19:45:00.000Z", "utc_arrival": "2023-04-17T17:45:00.000Z", "local_departure": "2023-04-17T16:15:00.000Z", "utc_departure": "2023-04-17T14:15:00.000Z"}, {"id": "0b770a224c2c0000f97822f4_0|0a220b774c2f0000a02e0875_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 749.770769, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 228352.4758, "conversion": {"EUR": 597.771149, "HUF": 228352.4758}, "fare": {"adults": 114176.24, "children": 118573.02, "infants": 118573.02}, "bags_price": {"1": 71.736, "2": 143.5}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 6}, "airlines": ["FR"], "route": [{"id": "0b770a224c2c0000f97822f4_0", "combination_id": "0b770a224c2c0000f97822f4", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-23T10:15:00.000Z", "utc_arrival": "2023-05-23T08:15:00.000Z", "local_departure": "2023-05-23T06:55:00.000Z", "utc_departure": "2023-05-23T04:55:00.000Z"}, {"id": "0a220b774c2f0000a02e0875_0", "combination_id": "0a220b774c2f0000a02e0875", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-26T18:00:00.000Z", "utc_arrival": "2023-05-26T16:00:00.000Z", "local_departure": "2023-05-26T14:50:00.000Z", "utc_departure": "2023-05-26T12:50:00.000Z"}], "booking_token": "ES3TtFJ52w7A2Y_Tlol_hjrHiS1WAKZ7zpi-hs8PvWENxFcpgfmpGat_gkjFFNOVHCI6Za_t8xev0ctN1Ih9aptxIR4p-84n1lx6asONhx2VkK20av6HUSmhSZSIRkfTvXAsazupRI9SPX22BkkQ4rsDCicLGR0TCVvl-N8XreckBQcZ6w7TM8f88AC1iwRgw6mqZyKEN6Y3kSz0DzjAcUCu--TZ2rranvzMvNiwBNQ4v0DkUZ9i-vZ4Oq6lP7odTKeYsDK3j1RJOlC1R8U1ZnfcPOzI78bQZwUAKgNfHJ-3MG35MUQ2E3ssW3EnTz6SSohMoNMQNFzTTrAjAndN-BcRAUr1WDcvJsmwozcXecHi-vw76tDRWJjalAH2elFFymNNftE3SR_2xdtMX1A6AydL1C1NU5yAIbwDpCFdfEbcGBrskP8SAoKHlp8tJVJ4pP3kkWJOKd1BiUYwppmd-Qc3iG6wPHKmvb63E2ZwuMzXRMYhIX_Iik3Km1qRHcdXZz5lKzDkMD4CWGP2ZRiNjx6RdgE-RcQTAgEH9uY9TaoEJr9CQ0-EPT95YEA6D7K6iUrTAJIakB2kZXlc84VyzVronP23xMpITHiyW2CBBTXO4BuzBmlGcVYJwyi0BPkyE-UeyK8lLcHNip_LuGnBFB221biNvSt8ixwtAFzrWMz8kLEP9wrg3hS7IHp0spec9h664NhQIxvc9ah3cYRYZGVezgdNWgPKjbT1_o3u3OfU=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c2c0000f97822f4_0%7C0a220b774c2f0000a02e0875_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=ES3TtFJ52w7A2Y_Tlol_hjrHiS1WAKZ7zpi-hs8PvWENxFcpgfmpGat_gkjFFNOVHCI6Za_t8xev0ctN1Ih9aptxIR4p-84n1lx6asONhx2VkK20av6HUSmhSZSIRkfTvXAsazupRI9SPX22BkkQ4rsDCicLGR0TCVvl-N8XreckBQcZ6w7TM8f88AC1iwRgw6mqZyKEN6Y3kSz0DzjAcUCu--TZ2rranvzMvNiwBNQ4v0DkUZ9i-vZ4Oq6lP7odTKeYsDK3j1RJOlC1R8U1ZnfcPOzI78bQZwUAKgNfHJ-3MG35MUQ2E3ssW3EnTz6SSohMoNMQNFzTTrAjAndN-BcRAUr1WDcvJsmwozcXecHi-vw76tDRWJjalAH2elFFymNNftE3SR_2xdtMX1A6AydL1C1NU5yAIbwDpCFdfEbcGBrskP8SAoKHlp8tJVJ4pP3kkWJOKd1BiUYwppmd-Qc3iG6wPHKmvb63E2ZwuMzXRMYhIX_Iik3Km1qRHcdXZz5lKzDkMD4CWGP2ZRiNjx6RdgE-RcQTAgEH9uY9TaoEJr9CQ0-EPT95YEA6D7K6iUrTAJIakB2kZXlc84VyzVronP23xMpITHiyW2CBBTXO4BuzBmlGcVYJwyi0BPkyE-UeyK8lLcHNip_LuGnBFB221biNvSt8ixwtAFzrWMz8kLEP9wrg3hS7IHp0spec9h664NhQIxvc9ah3cYRYZGVezgdNWgPKjbT1_o3u3OfU=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-23T10:15:00.000Z", "utc_arrival": "2023-05-23T08:15:00.000Z", "local_departure": "2023-05-23T06:55:00.000Z", "utc_departure": "2023-05-23T04:55:00.000Z"}, {"id": "0b770a224c4c4c50e447c703_0|0b770a224c4c4c50e447c703_1", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 748.459753, "distance": 1975.87, "duration": {"departure": 11700, "return": 11400, "total": 23100}, "price": 228360.9999, "conversion": {"EUR": 597.793463, "HUF": 228360.9999}, "fare": {"adults": 114180.5, "children": 114180.5, "infants": 114180.5}, "bags_price": {"1": 78.4, "2": 176.4}, "baglimit": {"hand_height": 40, "hand_length": 56, "hand_weight": 10, "hand_width": 25, "hold_dimensions_sum": 158, "hold_height": 52, "hold_length": 78, "hold_weight": 23, "hold_width": 28, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 3, "personal_item_width": 15}, "availability": {"seats": 4}, "airlines": ["IB"], "route": [{"id": "0b770a224c4c4c50e447c703_0", "combination_id": "0b770a224c4c4c50e447c703", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "IB", "flight_no": 3279, "operating_carrier": "IB", "operating_flight_no": "3279", "fare_basis": "NDNNANB4", "fare_category": "M", "fare_classes": "N", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-24T18:50:00.000Z", "utc_arrival": "2023-06-24T16:50:00.000Z", "local_departure": "2023-06-24T15:35:00.000Z", "utc_departure": "2023-06-24T13:35:00.000Z"}, {"id": "0b770a224c4c4c50e447c703_1", "combination_id": "0b770a224c4c4c50e447c703", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "IB", "flight_no": 3278, "operating_carrier": "IB", "operating_flight_no": "3278", "fare_basis": "QDNNANB4", "fare_category": "M", "fare_classes": "Q", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-28T14:55:00.000Z", "utc_arrival": "2023-06-28T12:55:00.000Z", "local_departure": "2023-06-28T11:45:00.000Z", "utc_departure": "2023-06-28T09:45:00.000Z"}], "booking_token": "ExK2Io5SmoEIpQZPW7-a6ePko-uojdwyv3V3Ow5wYR4OauhHAj5PE_GcgZd5cLO_86Y7Nwqky741RlaEWGprzP4q3YH2im-WfGn0NfcGYslCitSGBin_7bkgncO4duZ45GnDP_vitQwRAL7N_kCj496A7U9A7Do9NFPDkunzTOEsHyaoYOySqEW-uMDlZybFLYe19xYnL--V6UuWGwz-kdT4oQUZr6lVI6djTswgGJfU6ggxRnbeP6sL0Nesa-T0QV0x82BiostV2GqJKl1eU_dtE8TFto2gLns7vu0nEin7kaVZwkVBfLx9UGoUGuHVg2cLZZhjNbuA3tbKKhQHE5PHRxJglq6wds8DvrV1aHZtrRJWorpqBt_imqy1hD17ZmRqvxtTQqxllNi0sOA6QGdrb7Qd-lCucGwww1pTYo-YZSXRFYMq3ESYcQzZYoNhbcqvbUNODXPcznl093yXe6amTy0Lbe-bzJRjkWarGJN2aOtI7AutJzFEqKh0leggUntAJcRMFAh27KpeLXKIgdXyk1pQ9xoIl-XURnBx3DcW8rmweJ_SbgFbxgcm-1VsKsT4BXFmVryIb7nDRJqNi-dYka8aRnZ5umlgpazce3x2n4DYtwJrBpTgn_0nulL4fMaXGjLP4kn0bvcguJkoK1TQ-jDUZ5wgMfUB6E5kVdUvjzRPS5lobyhj0yNSvnQZVJGihprEhbgdiMMIH5J7EDUu7iIG0DuXWrmveSeUuwP7j5PwIv-OyNz2jdDQspTXt", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c4c4c50e447c703_0%7C0b770a224c4c4c50e447c703_1&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=ExK2Io5SmoEIpQZPW7-a6ePko-uojdwyv3V3Ow5wYR4OauhHAj5PE_GcgZd5cLO_86Y7Nwqky741RlaEWGprzP4q3YH2im-WfGn0NfcGYslCitSGBin_7bkgncO4duZ45GnDP_vitQwRAL7N_kCj496A7U9A7Do9NFPDkunzTOEsHyaoYOySqEW-uMDlZybFLYe19xYnL--V6UuWGwz-kdT4oQUZr6lVI6djTswgGJfU6ggxRnbeP6sL0Nesa-T0QV0x82BiostV2GqJKl1eU_dtE8TFto2gLns7vu0nEin7kaVZwkVBfLx9UGoUGuHVg2cLZZhjNbuA3tbKKhQHE5PHRxJglq6wds8DvrV1aHZtrRJWorpqBt_imqy1hD17ZmRqvxtTQqxllNi0sOA6QGdrb7Qd-lCucGwww1pTYo-YZSXRFYMq3ESYcQzZYoNhbcqvbUNODXPcznl093yXe6amTy0Lbe-bzJRjkWarGJN2aOtI7AutJzFEqKh0leggUntAJcRMFAh27KpeLXKIgdXyk1pQ9xoIl-XURnBx3DcW8rmweJ_SbgFbxgcm-1VsKsT4BXFmVryIb7nDRJqNi-dYka8aRnZ5umlgpazce3x2n4DYtwJrBpTgn_0nulL4fMaXGjLP4kn0bvcguJkoK1TQ-jDUZ5wgMfUB6E5kVdUvjzRPS5lobyhj0yNSvnQZVJGihprEhbgdiMMIH5J7EDUu7iIG0DuXWrmveSeUuwP7j5PwIv-OyNz2jdDQspTXt", "facilitated_booking_available": true, "pnr_count": 1, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-24T18:50:00.000Z", "utc_arrival": "2023-06-24T16:50:00.000Z", "local_departure": "2023-06-24T15:35:00.000Z", "utc_departure": "2023-06-24T13:35:00.000Z"}, {"id": "0b770a224c484c4cc80c73d9_0|0b770a224c484c4cc80c73d9_1", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 748.459753, "distance": 1975.87, "duration": {"departure": 11700, "return": 11400, "total": 23100}, "price": 228360.9999, "conversion": {"EUR": 597.793463, "HUF": 228360.9999}, "fare": {"adults": 114180.5, "children": 114180.5, "infants": 114180.5}, "bags_price": {"1": 78.4, "2": 176.4}, "baglimit": {"hand_height": 40, "hand_length": 56, "hand_weight": 10, "hand_width": 25, "hold_dimensions_sum": 158, "hold_height": 52, "hold_length": 78, "hold_weight": 23, "hold_width": 28, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 3, "personal_item_width": 15}, "availability": {"seats": 3}, "airlines": ["IB"], "route": [{"id": "0b770a224c484c4cc80c73d9_0", "combination_id": "0b770a224c484c4cc80c73d9", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "IB", "flight_no": 3279, "operating_carrier": "IB", "operating_flight_no": "3279", "fare_basis": "QDNNANB4", "fare_category": "M", "fare_classes": "Q", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-20T18:50:00.000Z", "utc_arrival": "2023-06-20T16:50:00.000Z", "local_departure": "2023-06-20T15:35:00.000Z", "utc_departure": "2023-06-20T13:35:00.000Z"}, {"id": "0b770a224c484c4cc80c73d9_1", "combination_id": "0b770a224c484c4cc80c73d9", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "IB", "flight_no": 3278, "operating_carrier": "IB", "operating_flight_no": "3278", "fare_basis": "NDNNANB4", "fare_category": "M", "fare_classes": "N", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-24T14:55:00.000Z", "utc_arrival": "2023-06-24T12:55:00.000Z", "local_departure": "2023-06-24T11:45:00.000Z", "utc_departure": "2023-06-24T09:45:00.000Z"}], "booking_token": "ERfE9S0-u74OShAzR8jUpeqf-sf_jj__M311A8EyzklOgEMhE5k_9dkItxppnQ-CRBFCi7GO8Jb19rZc1JXrpb0C1fwM3JLy9FHYcONcEjfAE7sbOZKhqddfh0lflAB4lRwYD8pqPx_FrAfhT0umw0mH-9naESBmdA_yffYitCEkVaZucEY-7ZcDO4NMbVFefDHHHpzoPsu-pQdxaIGPHZzbWNLOwj5PgKkSL50E5O6rOCpXtnsa37lhzWC1jYlBtdYLW5ONzYSG6QFf9MW8NpAQlCgTSzxknf3bTHcGKiDOOCDHRX-5tyi17Sfldy0w4g826frCxm6DDYgZXWdD5jMVHa5847yaefyJQYLsmlAHjpvtxRuBdy_DqK4h449N1c3CMn5LHBzeexNe9zMML7RkKOuOkb14WxyrZenm02Orai-6mSuK9odYJnbGw5ulk7avMnPhcoBP4sEPCCAI5dQ5dcY97L8e6db6bI1-NtMULqDAZBTgv_a8lQT-ZqfS84nrBDjmgC8w4BXKdlYHqf9KldGngOFwK0A5c_dw5fMyBlZ99KfZPdqpY1zpjMYbFGxeW80bC-erfG2dwiPyL1oV8m2vQJUtfP0srCRDVZOs-v8fzDIjVFYRHA0j4fzn8SIuLbmuFJawpPoXCeFhbgumJdthuzLACCmgwg_q-AZF1386LeTJKGyd5mr0L0Tw0l4GfInWYdSDMbaPHEfoOPdBDz3kzu14DX46r6py62foLmX4gqHIAqGl3HeO0ObQH", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c484c4cc80c73d9_0%7C0b770a224c484c4cc80c73d9_1&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=ERfE9S0-u74OShAzR8jUpeqf-sf_jj__M311A8EyzklOgEMhE5k_9dkItxppnQ-CRBFCi7GO8Jb19rZc1JXrpb0C1fwM3JLy9FHYcONcEjfAE7sbOZKhqddfh0lflAB4lRwYD8pqPx_FrAfhT0umw0mH-9naESBmdA_yffYitCEkVaZucEY-7ZcDO4NMbVFefDHHHpzoPsu-pQdxaIGPHZzbWNLOwj5PgKkSL50E5O6rOCpXtnsa37lhzWC1jYlBtdYLW5ONzYSG6QFf9MW8NpAQlCgTSzxknf3bTHcGKiDOOCDHRX-5tyi17Sfldy0w4g826frCxm6DDYgZXWdD5jMVHa5847yaefyJQYLsmlAHjpvtxRuBdy_DqK4h449N1c3CMn5LHBzeexNe9zMML7RkKOuOkb14WxyrZenm02Orai-6mSuK9odYJnbGw5ulk7avMnPhcoBP4sEPCCAI5dQ5dcY97L8e6db6bI1-NtMULqDAZBTgv_a8lQT-ZqfS84nrBDjmgC8w4BXKdlYHqf9KldGngOFwK0A5c_dw5fMyBlZ99KfZPdqpY1zpjMYbFGxeW80bC-erfG2dwiPyL1oV8m2vQJUtfP0srCRDVZOs-v8fzDIjVFYRHA0j4fzn8SIuLbmuFJawpPoXCeFhbgumJdthuzLACCmgwg_q-AZF1386LeTJKGyd5mr0L0Tw0l4GfInWYdSDMbaPHEfoOPdBDz3kzu14DX46r6py62foLmX4gqHIAqGl3HeO0ObQH", "facilitated_booking_available": true, "pnr_count": 1, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-20T18:50:00.000Z", "utc_arrival": "2023-06-20T16:50:00.000Z", "local_departure": "2023-06-20T15:35:00.000Z", "utc_departure": "2023-06-20T13:35:00.000Z"}, {"id": "0b770a224c05000004bc72da_0|0a220b774c0800003a297c03_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 750.455329, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 228613.9822, "conversion": {"EUR": 598.455709, "HUF": 228613.9822}, "fare": {"adults": 114306.99, "children": 114306.99, "infants": 114306.99}, "bags_price": {"1": 81.634, "2": 163.254}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 6}, "airlines": ["FR"], "route": [{"id": "0b770a224c05000004bc72da_0", "combination_id": "0b770a224c05000004bc72da", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-14T21:45:00.000Z", "utc_arrival": "2023-04-14T19:45:00.000Z", "local_departure": "2023-04-14T18:25:00.000Z", "utc_departure": "2023-04-14T16:25:00.000Z"}, {"id": "0a220b774c0800003a297c03_0", "combination_id": "0a220b774c0800003a297c03", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-17T10:15:00.000Z", "utc_arrival": "2023-04-17T08:15:00.000Z", "local_departure": "2023-04-17T07:05:00.000Z", "utc_departure": "2023-04-17T05:05:00.000Z"}], "booking_token": "E4HIJzZPP1cGr6I8GgB3zATvPqIxxrr2VVVj3ORxfl2igkZq7TEeRtcLrPxY70XXyaRs2mJsdq7iFDjVQZac4Y_FKS7PVwdVtztUjjI-Oon-FjltDE4PRiTc8L6MvdS0kmZ-L1LZMbA_hJSQ8QZi6XMiHcmoBtM75PAKwGy2W6Firi1-njtjktL9Pt6ruGOIWBT2PKgQDPOPfOTGvdyZMGb7xWnJ-nbChpzFSY31_xovTrrEESLG7pGFfUeGx45kIzhsP9YdUmrAJi0GjUpWMWcZNr5lpCoAraBSuQsCxD0SDojir2KI8rAfOCID8gVmQg3VHikrGMIULHWzg3XvDm35dBHdDrXPjeEVfo4zojEP0Cmv_V9W8KBJPUNI77w1rLDNhFp2N8SBay90rzr4TTUQJ8zN1WxTdcpToJyy3XlRbl8t-KPVUk6uNKAJnJx1BdrolZhybFSmYLSwpZRdynmLQmMg2nTl77V8Zp8GyQo8bJmq6LoW0Lia0PVf6RD9UqWfwFmgNs6OHwUwvffSo8q4OeeV5LrrL_HvdBCo_eZzJuGWggqd2EwGtPE7OJYEB3rAJeGqXwZQRYoqj2Jmt2LdjqxoyxVEV5rbUOuT12OExPdfHJveBS6mlVpsF23TvI3khj7Es3YO_DGqu4MZb9vKr7ovOeVLtAOn4P0qCRSC0nLYCRjrEohpHQlcQ5P5zgAdKGww6DNOCq34WwUDMow==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c05000004bc72da_0%7C0a220b774c0800003a297c03_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=E4HIJzZPP1cGr6I8GgB3zATvPqIxxrr2VVVj3ORxfl2igkZq7TEeRtcLrPxY70XXyaRs2mJsdq7iFDjVQZac4Y_FKS7PVwdVtztUjjI-Oon-FjltDE4PRiTc8L6MvdS0kmZ-L1LZMbA_hJSQ8QZi6XMiHcmoBtM75PAKwGy2W6Firi1-njtjktL9Pt6ruGOIWBT2PKgQDPOPfOTGvdyZMGb7xWnJ-nbChpzFSY31_xovTrrEESLG7pGFfUeGx45kIzhsP9YdUmrAJi0GjUpWMWcZNr5lpCoAraBSuQsCxD0SDojir2KI8rAfOCID8gVmQg3VHikrGMIULHWzg3XvDm35dBHdDrXPjeEVfo4zojEP0Cmv_V9W8KBJPUNI77w1rLDNhFp2N8SBay90rzr4TTUQJ8zN1WxTdcpToJyy3XlRbl8t-KPVUk6uNKAJnJx1BdrolZhybFSmYLSwpZRdynmLQmMg2nTl77V8Zp8GyQo8bJmq6LoW0Lia0PVf6RD9UqWfwFmgNs6OHwUwvffSo8q4OeeV5LrrL_HvdBCo_eZzJuGWggqd2EwGtPE7OJYEB3rAJeGqXwZQRYoqj2Jmt2LdjqxoyxVEV5rbUOuT12OExPdfHJveBS6mlVpsF23TvI3khj7Es3YO_DGqu4MZb9vKr7ovOeVLtAOn4P0qCRSC0nLYCRjrEohpHQlcQ5P5zgAdKGww6DNOCq34WwUDMow==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-04-14T21:45:00.000Z", "utc_arrival": "2023-04-14T19:45:00.000Z", "local_departure": "2023-04-14T18:25:00.000Z", "utc_departure": "2023-04-14T16:25:00.000Z"}, {"id": "0b770a224c2f0000c413678f_0|0a220b774c320000e133d3ca_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 753.31118, "distance": 1975.87, "duration": {"departure": 12600, "return": 11400, "total": 24000}, "price": 228686.2544, "conversion": {"EUR": 598.6449, "HUF": 228686.2544}, "fare": {"adults": 114343.13, "children": 114343.13, "infants": 114343.13}, "bags_price": {"1": 90.622, "2": 181.244}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 2}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224c2f0000c413678f_0", "combination_id": "0b770a224c2f0000c413678f", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-26T19:45:00.000Z", "utc_arrival": "2023-05-26T17:45:00.000Z", "local_departure": "2023-05-26T16:15:00.000Z", "utc_departure": "2023-05-26T14:15:00.000Z"}, {"id": "0a220b774c320000e133d3ca_0", "combination_id": "0a220b774c320000e133d3ca", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-29T10:15:00.000Z", "utc_arrival": "2023-05-29T08:15:00.000Z", "local_departure": "2023-05-29T07:05:00.000Z", "utc_departure": "2023-05-29T05:05:00.000Z"}], "booking_token": "EegpxEA7b_SpoOB1_vUSagRHqJTdWD3UcW7VkHlGJoJqCK5pTu8ODkB1gyagPAqBtrX5grEu2CGS-S7kPdSrdin-eWkNNPgRdt-_CXziS9E6Mcc3vLlbOLGBdFDKIHaJ3A4gpW51ZWfoYgov-vwaKh9BhXR6yB5AizOwcIHS2BtBgPOsBSKp8WERdDJCv4nC1_lZjcafomOms9cdgylArs3SK2fdAGo9J4rIP8Fw0_KRoXxmSt5UlYatOXWbq69fmtT0TbeCsbpCiyFgBinSl_VLWQuZrmE1RWgU5HHxOiRuvVzdpdSK8atjSwX6YpLwMHWcqynJEXW1dyPgTYotEgojFk-zYwDX_T_U3hg7xrqPiV_FpCztk-i6Ej-nZgCQNLXxln0Hr8-N0Ql1Me_J5Vc_U56nTR5_6BDjQfuoEgWLF8Yl3HmULtVDXSpJk-scojBNgOVDzNazsEfDN8V3Zkb4jr0zqWlZBqHdGGKeTqbAWo0eorkyn9JjDIMxVvM-8zYaBi3mHbgtPhFKYQcuLugieZDkLnaTMz2MPb_yYZuNxLxAHboNCWiAthbHm0hEHPRAydJrUhS6LJmnJ4pSBvWcK8yfqKZTkysShWU7fdH7_XFGfbAuE3GD3kfTI4Z8LKm0zq16GHuydZAuTA_Fux2lIvYfleJuV8-xXUX-D0F5-DZ5HATSma-nTcHgWX_YxbkKLQvQmqdQEswbxLssaH6v3cNEWesaMObfjDBvNqenBgFpVHAn5DMwyy1T34zfV", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c2f0000c413678f_0%7C0a220b774c320000e133d3ca_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EegpxEA7b_SpoOB1_vUSagRHqJTdWD3UcW7VkHlGJoJqCK5pTu8ODkB1gyagPAqBtrX5grEu2CGS-S7kPdSrdin-eWkNNPgRdt-_CXziS9E6Mcc3vLlbOLGBdFDKIHaJ3A4gpW51ZWfoYgov-vwaKh9BhXR6yB5AizOwcIHS2BtBgPOsBSKp8WERdDJCv4nC1_lZjcafomOms9cdgylArs3SK2fdAGo9J4rIP8Fw0_KRoXxmSt5UlYatOXWbq69fmtT0TbeCsbpCiyFgBinSl_VLWQuZrmE1RWgU5HHxOiRuvVzdpdSK8atjSwX6YpLwMHWcqynJEXW1dyPgTYotEgojFk-zYwDX_T_U3hg7xrqPiV_FpCztk-i6Ej-nZgCQNLXxln0Hr8-N0Ql1Me_J5Vc_U56nTR5_6BDjQfuoEgWLF8Yl3HmULtVDXSpJk-scojBNgOVDzNazsEfDN8V3Zkb4jr0zqWlZBqHdGGKeTqbAWo0eorkyn9JjDIMxVvM-8zYaBi3mHbgtPhFKYQcuLugieZDkLnaTMz2MPb_yYZuNxLxAHboNCWiAthbHm0hEHPRAydJrUhS6LJmnJ4pSBvWcK8yfqKZTkysShWU7fdH7_XFGfbAuE3GD3kfTI4Z8LKm0zq16GHuydZAuTA_Fux2lIvYfleJuV8-xXUX-D0F5-DZ5HATSma-nTcHgWX_YxbkKLQvQmqdQEswbxLssaH6v3cNEWesaMObfjDBvNqenBgFpVHAn5DMwyy1T34zfV", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-26T19:45:00.000Z", "utc_arrival": "2023-05-26T17:45:00.000Z", "local_departure": "2023-05-26T16:15:00.000Z", "utc_departure": "2023-05-26T14:15:00.000Z"}, {"id": "0b770a224c4b0000ee8a8a37_0|0a220b774c4e0000de14d559_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 752.035387, "distance": 1975.87, "duration": {"departure": 11700, "return": 11700, "total": 23400}, "price": 229217.5746, "conversion": {"EUR": 600.035767, "HUF": 229217.5746}, "fare": {"adults": 114608.79, "children": 117377.12, "infants": 117377.12}, "bags_price": {"1": 97.118, "2": 204.036}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 158, "hold_height": 52, "hold_length": 78, "hold_weight": 20, "hold_width": 28, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 3, "personal_item_width": 15}, "availability": {"seats": 7}, "airlines": ["W6", "IB"], "route": [{"id": "0b770a224c4b0000ee8a8a37_0", "combination_id": "0b770a224c4b0000ee8a8a37", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "IB", "flight_no": 3279, "operating_carrier": "IB", "operating_flight_no": "3279", "fare_basis": "QWNNAOB4", "fare_category": "M", "fare_classes": "Q", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-23T18:50:00.000Z", "utc_arrival": "2023-06-23T16:50:00.000Z", "local_departure": "2023-06-23T15:35:00.000Z", "utc_departure": "2023-06-23T13:35:00.000Z"}, {"id": "0a220b774c4e0000de14d559_0", "combination_id": "0a220b774c4e0000de14d559", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IJREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-26T23:45:00.000Z", "utc_arrival": "2023-06-26T21:45:00.000Z", "local_departure": "2023-06-26T20:30:00.000Z", "utc_departure": "2023-06-26T18:30:00.000Z"}], "booking_token": "EIGv4nhC5M5NxpE22p_NUTeTuGhXcNLQkFaGYwRrY24MBmpMlarGzzRCdw_vNSUkIr7wPHuSbvcALpsdJ2fZDKXgPGNo_eAMHRDUnJU686-R68XZtNkrbANtV4DFSKVG0D4bpuTucHNKNpsO2zHCSxzgdVDFDiUXGzz6v30iWEALW3AUhJXr0CVS3nv-fhDNTjbjuZXfhyuTpd5NofBMo0LulRbBAq9OnFnDZ7dfJbLezyne549jQhIlkBAiuZbBaAk1eaSDkWMHfRwuq9VahSoh_qB3hkWrOmsFzRDsGgPMPRtNI3m7WlOawr7p9oT23FJGa_Eb0QVY1fmK7Qldurh5KPX-4yjfjVihB0kDw2_XhPDMAL4NM9WOQKxfTdUd-SXY80sstVo_Hko80FnU29rDMqzXGOPH97ZMnESxsDcN4PLl9uqc_un7jR0MzRJvC5lUjAcQRbCwKGLLi8FiUnr_idLbU9rPMOJH-icY4Ub3vEpaO_sUxuTc6Aj-n8O3w1AEHAQ7SdQgq1KsyTmoHic0m9qmiUvvRajXr25NnvxtyXGUuBD1W6JdO41Yrtlz90KYDA6VoUioY1TGutEwiEFa8Rv7I5T_JFTYZ8i6RoDKG9xKk75UXKpsAwb3Qz3I3OW-o1W8pQ-oO0RSxULUbJy9zrMslwoaSp8ydhZRlHoT0qLcfeRESN-XaUd62xsQCb3xxlV4V6M79Is_MBHxPR-CowXamfbDm_f0iO_Zcs2hoAZ9ivmWzFacbsOc93U2ZF6ByVE9AMRtDLZT15bSsD4dwhgdToIJEYN5o_JloHeM6MovVVGLjYLpkH1snkIK0zCbO4LyHPI7NhaQhUaS9mQ==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c4b0000ee8a8a37_0%7C0a220b774c4e0000de14d559_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EIGv4nhC5M5NxpE22p_NUTeTuGhXcNLQkFaGYwRrY24MBmpMlarGzzRCdw_vNSUkIr7wPHuSbvcALpsdJ2fZDKXgPGNo_eAMHRDUnJU686-R68XZtNkrbANtV4DFSKVG0D4bpuTucHNKNpsO2zHCSxzgdVDFDiUXGzz6v30iWEALW3AUhJXr0CVS3nv-fhDNTjbjuZXfhyuTpd5NofBMo0LulRbBAq9OnFnDZ7dfJbLezyne549jQhIlkBAiuZbBaAk1eaSDkWMHfRwuq9VahSoh_qB3hkWrOmsFzRDsGgPMPRtNI3m7WlOawr7p9oT23FJGa_Eb0QVY1fmK7Qldurh5KPX-4yjfjVihB0kDw2_XhPDMAL4NM9WOQKxfTdUd-SXY80sstVo_Hko80FnU29rDMqzXGOPH97ZMnESxsDcN4PLl9uqc_un7jR0MzRJvC5lUjAcQRbCwKGLLi8FiUnr_idLbU9rPMOJH-icY4Ub3vEpaO_sUxuTc6Aj-n8O3w1AEHAQ7SdQgq1KsyTmoHic0m9qmiUvvRajXr25NnvxtyXGUuBD1W6JdO41Yrtlz90KYDA6VoUioY1TGutEwiEFa8Rv7I5T_JFTYZ8i6RoDKG9xKk75UXKpsAwb3Qz3I3OW-o1W8pQ-oO0RSxULUbJy9zrMslwoaSp8ydhZRlHoT0qLcfeRESN-XaUd62xsQCb3xxlV4V6M79Is_MBHxPR-CowXamfbDm_f0iO_Zcs2hoAZ9ivmWzFacbsOc93U2ZF6ByVE9AMRtDLZT15bSsD4dwhgdToIJEYN5o_JloHeM6MovVVGLjYLpkH1snkIK0zCbO4LyHPI7NhaQhUaS9mQ==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-23T18:50:00.000Z", "utc_arrival": "2023-06-23T16:50:00.000Z", "local_departure": "2023-06-23T15:35:00.000Z", "utc_departure": "2023-06-23T13:35:00.000Z"}, {"id": "0b770a224c360000605964d6_0|0a220b774c3a0000fea059a3_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 752.288458, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 229314.2494, "conversion": {"EUR": 600.288838, "HUF": 229314.2494}, "fare": {"adults": 114657.12, "children": 114657.12, "infants": 114657.12}, "bags_price": {"1": 76.706, "2": 163.212}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 158, "hold_height": 52, "hold_length": 78, "hold_weight": 20, "hold_width": 28, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 3, "personal_item_width": 15}, "availability": {"seats": 2}, "airlines": ["FR", "IB"], "route": [{"id": "0b770a224c360000605964d6_0", "combination_id": "0b770a224c360000605964d6", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-02T21:45:00.000Z", "utc_arrival": "2023-06-02T19:45:00.000Z", "local_departure": "2023-06-02T18:25:00.000Z", "utc_departure": "2023-06-02T16:25:00.000Z"}, {"id": "0a220b774c3a0000fea059a3_0", "combination_id": "0a220b774c3a0000fea059a3", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "IB", "flight_no": 3278, "operating_carrier": "IB", "operating_flight_no": "3278", "fare_basis": "VZNNAOB4", "fare_category": "M", "fare_classes": "V", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-06T14:55:00.000Z", "utc_arrival": "2023-06-06T12:55:00.000Z", "local_departure": "2023-06-06T11:45:00.000Z", "utc_departure": "2023-06-06T09:45:00.000Z"}], "booking_token": "EaawDqMEI1TpD1ueGxlqiapo_eTiusXsU1ms9RzU2fDUW_iXJDvXj5im8lw3homQNGQMD6WfiAYu5pWUxq5vnHxPSKN8hT7QSbauYpb4gi9-C3o6w8lh0ZGmB0xW1N2jYuJuRCXgQfcnSdk-4o76YMCmOTfYny7_TsJA9GTYv9QSPrNGORluBvcPBYdjZq_vajMTyxMQkn59NrL2Y-HKFjMwWLYCbtQ_I1hM1RGw-fb67ayyiZL7K_mOmDxt0aY8E0tWwxnHmG498zz9KwEVFy9TTbvlTWExxre-cdDuZpWRPAPPWduLv-pNaLzl0i1UB1rKeRkl8glWTYLUMT4MlQ56pvk5gNEf1omrnUpkkhq9V3f028wgyVjlVQXanXFyXb1V5S4ZJxLN-F5zONrVG1dPwLNxOMIb4E7G6czVLNs7SVMtjfu0FnHJsDXc7Yuj_XqFriejN7O7d1EuQWtJee3YdNQhqAx0_m6IoH-RTFFy6NjOW1iqBeKbMXpcwvGVdgRw4zUyicKZNJvuCHPj0QyHAQAh0iVdnjcbi_zbsRAVi80W-aF7RlYqBDUKfuqMMDo75WsylZWx-NxOi_FGZeG3WBDK5xBRakv1bK__mr3f06lFy6QDshPfwlzwG-QaJTQesvzoVswnwrwIXP6PyCCEcJ3XDhOTt2cPRGDoi-R6BQuc49TdgCkOb7dcUAY3hjckcK28Jj2BJDsQr-J_2H3jCAuMO0dqSDq8ibKYNnRPI5yvXZtest7LpQDAzzKmZFx9zg6GfUc9PMgJSS8nZ5p-VofuuOglSh5SCyTmaI34=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c360000605964d6_0%7C0a220b774c3a0000fea059a3_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EaawDqMEI1TpD1ueGxlqiapo_eTiusXsU1ms9RzU2fDUW_iXJDvXj5im8lw3homQNGQMD6WfiAYu5pWUxq5vnHxPSKN8hT7QSbauYpb4gi9-C3o6w8lh0ZGmB0xW1N2jYuJuRCXgQfcnSdk-4o76YMCmOTfYny7_TsJA9GTYv9QSPrNGORluBvcPBYdjZq_vajMTyxMQkn59NrL2Y-HKFjMwWLYCbtQ_I1hM1RGw-fb67ayyiZL7K_mOmDxt0aY8E0tWwxnHmG498zz9KwEVFy9TTbvlTWExxre-cdDuZpWRPAPPWduLv-pNaLzl0i1UB1rKeRkl8glWTYLUMT4MlQ56pvk5gNEf1omrnUpkkhq9V3f028wgyVjlVQXanXFyXb1V5S4ZJxLN-F5zONrVG1dPwLNxOMIb4E7G6czVLNs7SVMtjfu0FnHJsDXc7Yuj_XqFriejN7O7d1EuQWtJee3YdNQhqAx0_m6IoH-RTFFy6NjOW1iqBeKbMXpcwvGVdgRw4zUyicKZNJvuCHPj0QyHAQAh0iVdnjcbi_zbsRAVi80W-aF7RlYqBDUKfuqMMDo75WsylZWx-NxOi_FGZeG3WBDK5xBRakv1bK__mr3f06lFy6QDshPfwlzwG-QaJTQesvzoVswnwrwIXP6PyCCEcJ3XDhOTt2cPRGDoi-R6BQuc49TdgCkOb7dcUAY3hjckcK28Jj2BJDsQr-J_2H3jCAuMO0dqSDq8ibKYNnRPI5yvXZtest7LpQDAzzKmZFx9zg6GfUc9PMgJSS8nZ5p-VofuuOglSh5SCyTmaI34=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-02T21:45:00.000Z", "utc_arrival": "2023-06-02T19:45:00.000Z", "local_departure": "2023-06-02T18:25:00.000Z", "utc_departure": "2023-06-02T16:25:00.000Z"}, {"id": "0b770a224c0c00004f039f60_0|0a220b774c10000085c9a6d8_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 752.769619, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 229498.056, "conversion": {"EUR": 600.769999, "HUF": 229498.056}, "fare": {"adults": 114749.03, "children": 114749.03, "infants": 114749.03}, "bags_price": {"1": 80.01, "2": 160.006}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 5}, "airlines": ["FR"], "route": [{"id": "0b770a224c0c00004f039f60_0", "combination_id": "0b770a224c0c00004f039f60", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-21T21:45:00.000Z", "utc_arrival": "2023-04-21T19:45:00.000Z", "local_departure": "2023-04-21T18:25:00.000Z", "utc_departure": "2023-04-21T16:25:00.000Z"}, {"id": "0a220b774c10000085c9a6d8_0", "combination_id": "0a220b774c10000085c9a6d8", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-25T14:05:00.000Z", "utc_arrival": "2023-04-25T12:05:00.000Z", "local_departure": "2023-04-25T10:55:00.000Z", "utc_departure": "2023-04-25T08:55:00.000Z"}], "booking_token": "EXOHCmXMKmgg7sjQXeAEFuurshpVVmjsnbEfF_8xoelB9m6EJYmGXIdRYAHffVsIjEstMk7X4oq_70c-YJQU7vhRkBPHT1nci4VnOF-kPT9-mOgP7d8GNVlQZlWL_1sCxZXRvhQXWrr9TT0FZPiLx8y7wfhnE5NLaJnVP45l1LkEqVC-LgFFc71_kZXtY_-MS8HZcRgUNF4meJ_CcOoY5aOhomAEFJ2WdKRCS9EHHZDUpazbvQCnK6-zMlJ2tdqvUoCenVy0RnsP7fPtM8C_q4LkIMTGf5JaJYLTuNz1FLDk5UJwjkYhrGR2V10RD8lCho5EqM2EucXo1FCS3fGCmSh-muu-5keLIMrH_WTU54kQ-AF5jH5yKzIyL5-lsyAhnHtn5lATQTyKf-J8QXyEpgeiEs4Bkpd7Tjk5zgRVoQBw9sJ2qTYFQwWlYjk2_6sOYbWCU_5IfSy4zfZ4LkYiSzV1WOCuOlR2ppvx-iSc2uhMN6U1qc-U4sVkMqHTKETi52uTaHovZ_3flTuX0YA8jAJj1be7Q-USmcfEZScR7UXLUDShunUC6o-_Hhy2439OFpBnSxIpiSOuH9GmgvuJiD-aVnjzvJMjSMLQ3-0Bkay4oBYte-MkTEsmoeJHOb72uZRepGPnAJ0bk50k4MPV0zXVLiSzjhG-2m5JoORFoKpPKfMH2HdERGL-Gm5Qlra-KNnjV9HET0MOYDL95Y1mQlkMdqqBeKDkES5BhmuoJazBzYRt03pSwlixj0v3DLS9YgC5LlmfxxjLuBoOivPZsQQ==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c0c00004f039f60_0%7C0a220b774c10000085c9a6d8_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EXOHCmXMKmgg7sjQXeAEFuurshpVVmjsnbEfF_8xoelB9m6EJYmGXIdRYAHffVsIjEstMk7X4oq_70c-YJQU7vhRkBPHT1nci4VnOF-kPT9-mOgP7d8GNVlQZlWL_1sCxZXRvhQXWrr9TT0FZPiLx8y7wfhnE5NLaJnVP45l1LkEqVC-LgFFc71_kZXtY_-MS8HZcRgUNF4meJ_CcOoY5aOhomAEFJ2WdKRCS9EHHZDUpazbvQCnK6-zMlJ2tdqvUoCenVy0RnsP7fPtM8C_q4LkIMTGf5JaJYLTuNz1FLDk5UJwjkYhrGR2V10RD8lCho5EqM2EucXo1FCS3fGCmSh-muu-5keLIMrH_WTU54kQ-AF5jH5yKzIyL5-lsyAhnHtn5lATQTyKf-J8QXyEpgeiEs4Bkpd7Tjk5zgRVoQBw9sJ2qTYFQwWlYjk2_6sOYbWCU_5IfSy4zfZ4LkYiSzV1WOCuOlR2ppvx-iSc2uhMN6U1qc-U4sVkMqHTKETi52uTaHovZ_3flTuX0YA8jAJj1be7Q-USmcfEZScR7UXLUDShunUC6o-_Hhy2439OFpBnSxIpiSOuH9GmgvuJiD-aVnjzvJMjSMLQ3-0Bkay4oBYte-MkTEsmoeJHOb72uZRepGPnAJ0bk50k4MPV0zXVLiSzjhG-2m5JoORFoKpPKfMH2HdERGL-Gm5Qlra-KNnjV9HET0MOYDL95Y1mQlkMdqqBeKDkES5BhmuoJazBzYRt03pSwlixj0v3DLS9YgC5LlmfxxjLuBoOivPZsQQ==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-04-21T21:45:00.000Z", "utc_arrival": "2023-04-21T19:45:00.000Z", "local_departure": "2023-04-21T18:25:00.000Z", "utc_departure": "2023-04-21T16:25:00.000Z"}, {"id": "0b770a224bfa0000f711598b_0|0a220b774bfe000002ec78b7_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 755.845165, "distance": 1975.87, "duration": {"departure": 12600, "return": 11400, "total": 24000}, "price": 229654.2532, "conversion": {"EUR": 601.178885, "HUF": 229654.2532}, "fare": {"adults": 114827.13, "children": 114827.13, "infants": 114827.13}, "bags_price": {"1": 112.91, "2": 225.806}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 5}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224bfa0000f711598b_0", "combination_id": "0b770a224bfa0000f711598b", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "JKREG", "fare_category": "M", "fare_classes": "J", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-03T19:45:00.000Z", "utc_arrival": "2023-04-03T17:45:00.000Z", "local_departure": "2023-04-03T16:15:00.000Z", "utc_departure": "2023-04-03T14:15:00.000Z"}, {"id": "0a220b774bfe000002ec78b7_0", "combination_id": "0a220b774bfe000002ec78b7", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-07T18:00:00.000Z", "utc_arrival": "2023-04-07T16:00:00.000Z", "local_departure": "2023-04-07T14:50:00.000Z", "utc_departure": "2023-04-07T12:50:00.000Z"}], "booking_token": "EM7DBvY3TCaI60DoPryBGz6FX0C0LSr6HSFB6zr5aC-jiJA7go4yQzdhwPTwKMBrP7GJeNGaAL6Bjcd1IAg2fHWiXQTI--ipQqib3GWeQifnm472Zgb-y2rtT_h_ZnmFxVN2JqLkcYfJsiCnYYy-BlnyH0aVeNj250rZX5I_QxZsdsxkAYT5R9aVVWKmQAfsQ7Mev7MhEenuzsQVR-TvtgRemTj8usvNG02HPspHT2MxSuWpkKOIcGz3ARKX_7LUquKiyIs3g3-G-DKg6gLKaLGRUtFKZCZNZj92_EnFO15y5ofi8FmAy2XgUGOevXVj46WuPg6hEc7Vkl0zezEm70Im1ItDRUSvZrEkAAvbpb3kKlCFA7g2-SeJzx4zsbzBscGl0uUDYeUuKtGPa7bFEviPyA7OsB_45VJvc3nGpm33rGe7t68_tPgThpOfsFiGv8lZajXPg0MXOb5Rah1GFLt1We0aGwUGcsfwOUDKPKeJoaHI-iKHygGcGBHn-kqk0xQTmQmxu3ft8R0bK8THi3wKJJvenblY34dDTkfYRKD7BHk_2TmU-SPSIwxvWdYsDqdjnycI7py4TPTQ7QD05dFFydvKVVKgqjvXNaWMCjPGtF45LiDRMS5EGJlL6316UYEfL6pHvdwIbD94VHJdq_7kFS_6gS7AFMadfPBTZ908PYDPJXWhDzHmanStkCXbyRJCBa-rI63ymyhDi_RCLITKkpExWPboKIi4MIEp0C97OYbOcIF_kwHezkB8joWRHc7Ef93rG6R7GYcoNWKIlWw==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224bfa0000f711598b_0%7C0a220b774bfe000002ec78b7_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EM7DBvY3TCaI60DoPryBGz6FX0C0LSr6HSFB6zr5aC-jiJA7go4yQzdhwPTwKMBrP7GJeNGaAL6Bjcd1IAg2fHWiXQTI--ipQqib3GWeQifnm472Zgb-y2rtT_h_ZnmFxVN2JqLkcYfJsiCnYYy-BlnyH0aVeNj250rZX5I_QxZsdsxkAYT5R9aVVWKmQAfsQ7Mev7MhEenuzsQVR-TvtgRemTj8usvNG02HPspHT2MxSuWpkKOIcGz3ARKX_7LUquKiyIs3g3-G-DKg6gLKaLGRUtFKZCZNZj92_EnFO15y5ofi8FmAy2XgUGOevXVj46WuPg6hEc7Vkl0zezEm70Im1ItDRUSvZrEkAAvbpb3kKlCFA7g2-SeJzx4zsbzBscGl0uUDYeUuKtGPa7bFEviPyA7OsB_45VJvc3nGpm33rGe7t68_tPgThpOfsFiGv8lZajXPg0MXOb5Rah1GFLt1We0aGwUGcsfwOUDKPKeJoaHI-iKHygGcGBHn-kqk0xQTmQmxu3ft8R0bK8THi3wKJJvenblY34dDTkfYRKD7BHk_2TmU-SPSIwxvWdYsDqdjnycI7py4TPTQ7QD05dFFydvKVVKgqjvXNaWMCjPGtF45LiDRMS5EGJlL6316UYEfL6pHvdwIbD94VHJdq_7kFS_6gS7AFMadfPBTZ908PYDPJXWhDzHmanStkCXbyRJCBa-rI63ymyhDi_RCLITKkpExWPboKIi4MIEp0C97OYbOcIF_kwHezkB8joWRHc7Ef93rG6R7GYcoNWKIlWw==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-04-03T19:45:00.000Z", "utc_arrival": "2023-04-03T17:45:00.000Z", "local_departure": "2023-04-03T16:15:00.000Z", "utc_departure": "2023-04-03T14:15:00.000Z"}, {"id": "0b770a224c0b0000d52101c0_0|0a220b774c0f0000a1c65665_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 756.809133, "distance": 1975.87, "duration": {"departure": 12600, "return": 11400, "total": 24000}, "price": 230022.4952, "conversion": {"EUR": 602.142853, "HUF": 230022.4952}, "fare": {"adults": 115011.25, "children": 115011.25, "infants": 115011.25}, "bags_price": {"1": 115.906, "2": 231.812}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 5}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224c0b0000d52101c0_0", "combination_id": "0b770a224c0b0000d52101c0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "JKREG", "fare_category": "M", "fare_classes": "J", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-20T21:15:00.000Z", "utc_arrival": "2023-04-20T19:15:00.000Z", "local_departure": "2023-04-20T17:45:00.000Z", "utc_departure": "2023-04-20T15:45:00.000Z"}, {"id": "0a220b774c0f0000a1c65665_0", "combination_id": "0a220b774c0f0000a1c65665", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-24T10:15:00.000Z", "utc_arrival": "2023-04-24T08:15:00.000Z", "local_departure": "2023-04-24T07:05:00.000Z", "utc_departure": "2023-04-24T05:05:00.000Z"}], "booking_token": "EdVDOqQUUzrOe-BydExaOF1FYNNWD8-CezGfaaFB34n8h7MNhYfUbndfcVE8kLAiwJnykKuIvb2I_kJFphCOYtYFvzaH-60-SG7h_GIW-phW85EbNEi8SBVFTS3SfpzPgj7rdi9n4QQT5HW0xGnBeiHQcz2gDUh6m0hpfRysrGgyF5p9JUGJbCO4UZ_v0CepCjqLMgxLHZNbCoSQjZZBTdtdashIl0Jy_JvOl2q01RR_bS4lh9C4_GdWGvhkSjImLoKeaLkcpLbW0MUBviUjDgftkDWjHTM6qUBM5fQLk3_C3-dKpD9gRBUuD_MuuqSM8eHmHWhDZCPoJKcWjE2iob3fp2g8aAL4Y4YkzX7NPIB_mCOBV3JG748tvdGOcHM4VISr9Yi5b_aKtgezmfOPb92qn0LfIw6ZPNUtGN4vwnfxRqAoEs1KZjCd7Rgx8nGBDQfzkCgxTAZoLklQ86mR66nphbLsYp1pM64_3GrGUtJGgPu0mmQU6-_oDUdevKOjpVrVs7VgqeaXOsPnKzBwfeuB67Sp_VkiWgDaEBahSkoj_cLFNXSOhMlq7K82_ZsZTHeLDWl6IrpIaH_lcmv79rD3Icwt-6eXnej_2tvug1ow2T8ToJ70Tt2ozKuNnFPMM1s-qOWlzZ5UGkmUASTXeJJCGyNUUxScWJR_7WCkdnHTFjFvsUcbW1XIx-OVwG0VLSAJ31N7HM_weN00bx8u4xWSJ5TV7xXcROh3vFUA6C8h8UdEpBrTu_ovzOivTkIbQZ-3yA57s5CsBBuuQUjKQYIjiCsCGnIMqpRq0abZKCnE=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c0b0000d52101c0_0%7C0a220b774c0f0000a1c65665_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EdVDOqQUUzrOe-BydExaOF1FYNNWD8-CezGfaaFB34n8h7MNhYfUbndfcVE8kLAiwJnykKuIvb2I_kJFphCOYtYFvzaH-60-SG7h_GIW-phW85EbNEi8SBVFTS3SfpzPgj7rdi9n4QQT5HW0xGnBeiHQcz2gDUh6m0hpfRysrGgyF5p9JUGJbCO4UZ_v0CepCjqLMgxLHZNbCoSQjZZBTdtdashIl0Jy_JvOl2q01RR_bS4lh9C4_GdWGvhkSjImLoKeaLkcpLbW0MUBviUjDgftkDWjHTM6qUBM5fQLk3_C3-dKpD9gRBUuD_MuuqSM8eHmHWhDZCPoJKcWjE2iob3fp2g8aAL4Y4YkzX7NPIB_mCOBV3JG748tvdGOcHM4VISr9Yi5b_aKtgezmfOPb92qn0LfIw6ZPNUtGN4vwnfxRqAoEs1KZjCd7Rgx8nGBDQfzkCgxTAZoLklQ86mR66nphbLsYp1pM64_3GrGUtJGgPu0mmQU6-_oDUdevKOjpVrVs7VgqeaXOsPnKzBwfeuB67Sp_VkiWgDaEBahSkoj_cLFNXSOhMlq7K82_ZsZTHeLDWl6IrpIaH_lcmv79rD3Icwt-6eXnej_2tvug1ow2T8ToJ70Tt2ozKuNnFPMM1s-qOWlzZ5UGkmUASTXeJJCGyNUUxScWJR_7WCkdnHTFjFvsUcbW1XIx-OVwG0VLSAJ31N7HM_weN00bx8u4xWSJ5TV7xXcROh3vFUA6C8h8UdEpBrTu_ovzOivTkIbQZ-3yA57s5CsBBuuQUjKQYIjiCsCGnIMqpRq0abZKCnE=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-04-20T21:15:00.000Z", "utc_arrival": "2023-04-20T19:15:00.000Z", "local_departure": "2023-04-20T17:45:00.000Z", "utc_departure": "2023-04-20T15:45:00.000Z"}, {"id": "0b770a224c4400001cdf0063_0|0a220b774c48000056e1c9c9_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 759.177585, "distance": 1975.87, "duration": {"departure": 12600, "return": 11400, "total": 24000}, "price": 230927.2593, "conversion": {"EUR": 604.511305, "HUF": 230927.2593}, "fare": {"adults": 115463.63, "children": 118178.36, "infants": 118178.36}, "bags_price": {"1": 72.268, "2": 154.336}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 158, "hold_height": 52, "hold_length": 78, "hold_weight": 20, "hold_width": 28, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 3, "personal_item_width": 15}, "availability": {"seats": 3}, "airlines": ["W6", "IB"], "route": [{"id": "0b770a224c4400001cdf0063_0", "combination_id": "0b770a224c4400001cdf0063", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "HIREG", "fare_category": "M", "fare_classes": "H", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-16T19:45:00.000Z", "utc_arrival": "2023-06-16T17:45:00.000Z", "local_departure": "2023-06-16T16:15:00.000Z", "utc_departure": "2023-06-16T14:15:00.000Z"}, {"id": "0a220b774c48000056e1c9c9_0", "combination_id": "0a220b774c48000056e1c9c9", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "IB", "flight_no": 3278, "operating_carrier": "IB", "operating_flight_no": "3278", "fare_basis": "QDNNAOB4", "fare_category": "M", "fare_classes": "Q", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-20T14:55:00.000Z", "utc_arrival": "2023-06-20T12:55:00.000Z", "local_departure": "2023-06-20T11:45:00.000Z", "utc_departure": "2023-06-20T09:45:00.000Z"}], "booking_token": "EDe4yl1nil9rKc2OCzpjfFqrtFkOMXHazo_-DY02ME4lm68QiK2qLsiJiR9Uv4-qfRSM0-s3fDuzDFCdmNlz54SmXcPqn63sGmo8UVmtF2LrqD6A1xI7ibeHyCjRA1_cGCuPRhAbZrxVa9QNLmtlVdnhXiO93YgitYjQtZLwdMLMROH65sxEdAjQmPdIxFEsF7fp8zh89LKk35YRaZONcJahI2oC5vowZp2QgpjjfrGwPqFkLvl1hksRK2Mvnv4BVFYxBvpCY4iNZ12he1qasuZsv9YP4jvVAiWy8sE6EfiCdzGJVsv6W_WlR1XOZO33i7L8JsJKaSNof0fN-8V8TsBDNgxL7RCehQ_f33bbsgMJ9KN8h6e-GGxtFkdxBZ3OduWpi83XAUAl1-SH80D8wx4fkxGoH5qVTFHM6SQMjWiazSq0uQbTuHSIjk1rVWUaWAxCi98K9gEoPUnJd86ER6mgyGNdu7H5eHw9yzIfL8-4fdKW5fa2QJpR7dQkjz9ERqnnkMrxafvtZGshau-cLmYqhRLA69njdoEjwH872F2QkQ1zXTvXBYdHbevUSnzN034hQI_z95o3gjPl2dlOtMmYmr_7lR0JebfbyZ3C8hUppJ9wfJ4tf2SD904Tyfl2nwUELwQEZsxDQx5yrLy9hdTzxtnhyrBv_Wz5TZEjm1eVn-zuyzMhE-COD2SDxEwnNBZ8QUaS1BOuw2qhTgxSJ8OQOtRXFoegSfn9p6WhxAPP6NNaVSHEBmXcN308RY19czSDPOzdIqlLSVD36OZ7Eu9xYSwHS2d-PDsTarQIk7uoVwZ_t_swfXw8fa0CszSyoBk5Q7Yfy1B_JyFGCE4YsUQ==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c4400001cdf0063_0%7C0a220b774c48000056e1c9c9_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EDe4yl1nil9rKc2OCzpjfFqrtFkOMXHazo_-DY02ME4lm68QiK2qLsiJiR9Uv4-qfRSM0-s3fDuzDFCdmNlz54SmXcPqn63sGmo8UVmtF2LrqD6A1xI7ibeHyCjRA1_cGCuPRhAbZrxVa9QNLmtlVdnhXiO93YgitYjQtZLwdMLMROH65sxEdAjQmPdIxFEsF7fp8zh89LKk35YRaZONcJahI2oC5vowZp2QgpjjfrGwPqFkLvl1hksRK2Mvnv4BVFYxBvpCY4iNZ12he1qasuZsv9YP4jvVAiWy8sE6EfiCdzGJVsv6W_WlR1XOZO33i7L8JsJKaSNof0fN-8V8TsBDNgxL7RCehQ_f33bbsgMJ9KN8h6e-GGxtFkdxBZ3OduWpi83XAUAl1-SH80D8wx4fkxGoH5qVTFHM6SQMjWiazSq0uQbTuHSIjk1rVWUaWAxCi98K9gEoPUnJd86ER6mgyGNdu7H5eHw9yzIfL8-4fdKW5fa2QJpR7dQkjz9ERqnnkMrxafvtZGshau-cLmYqhRLA69njdoEjwH872F2QkQ1zXTvXBYdHbevUSnzN034hQI_z95o3gjPl2dlOtMmYmr_7lR0JebfbyZ3C8hUppJ9wfJ4tf2SD904Tyfl2nwUELwQEZsxDQx5yrLy9hdTzxtnhyrBv_Wz5TZEjm1eVn-zuyzMhE-COD2SDxEwnNBZ8QUaS1BOuw2qhTgxSJ8OQOtRXFoegSfn9p6WhxAPP6NNaVSHEBmXcN308RY19czSDPOzdIqlLSVD36OZ7Eu9xYSwHS2d-PDsTarQIk7uoVwZ_t_swfXw8fa0CszSyoBk5Q7Yfy1B_JyFGCE4YsUQ==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-16T19:45:00.000Z", "utc_arrival": "2023-06-16T17:45:00.000Z", "local_departure": "2023-06-16T16:15:00.000Z", "utc_departure": "2023-06-16T14:15:00.000Z"}, {"id": "0b770a224c3a0000c54ce2f2_0|0a220b774c3d0000a9239654_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 756.655179, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 230982.3653, "conversion": {"EUR": 604.655559, "HUF": 230982.3653}, "fare": {"adults": 115491.18, "children": 115491.18, "infants": 115491.18}, "bags_price": {"1": 75.068, "2": 159.95}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 158, "hold_height": 52, "hold_length": 78, "hold_weight": 20, "hold_width": 28, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 3, "personal_item_width": 15}, "availability": {"seats": 6}, "airlines": ["FR", "IB"], "route": [{"id": "0b770a224c3a0000c54ce2f2_0", "combination_id": "0b770a224c3a0000c54ce2f2", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-06T10:15:00.000Z", "utc_arrival": "2023-06-06T08:15:00.000Z", "local_departure": "2023-06-06T06:55:00.000Z", "utc_departure": "2023-06-06T04:55:00.000Z"}, {"id": "0a220b774c3d0000a9239654_0", "combination_id": "0a220b774c3d0000a9239654", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "IB", "flight_no": 3278, "operating_carrier": "IB", "operating_flight_no": "3278", "fare_basis": "VZNNAOB4", "fare_category": "M", "fare_classes": "V", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-09T14:55:00.000Z", "utc_arrival": "2023-06-09T12:55:00.000Z", "local_departure": "2023-06-09T11:45:00.000Z", "utc_departure": "2023-06-09T09:45:00.000Z"}], "booking_token": "Elcgh0lZk4w-Cd7QXTkVtquK4vphm8Ka7nrniw5pgkQDxaVcEJJc0NFg3Vb7MnGWhmW7iJuY2PFHinym0eQvAjgEpszA40SpExbaSkVfeUdMhgmKk2EeXf3xs9COuBBDbs86wIqINA5fwNGa0Aiex1UUMY8AGKpl_awGyE6Us60q9B6IoIN977F0jbD5_yqV50BQOkCqAdAehieynD1DAJWsEdk3s_DzCwgcjd5U5H8kfSN6gk1RnAXRzkpPpEwPgum8XUae-QX06NPT8mDFAC8702ILKYR7EhbgwFWZ6o-iorHIzbvziUVM81LvcWbNCCPAmRXWUyKZgd9b1bcS5n_jhc7nN6NWqeLy-z0bP3LQXqAkmNtpv4UjXO58wL_QW07PLuS5ohszs1eaBJ-ybl7c7EX3otx9wYSiPrB8opNt0GRHN6EQCa6d9hF4scnOkR2GSYv-_N82fMucTndPBtC-wO9V4PSyZ-vBT0Y2tmDe1tpQojX1p2SgccwBXd0pbAZ0xi3JtvoKAzABgI0eTUBhAurHnoL3yBNuGWJSspAcrBOnD8q2FaFYajZ0aHJSCoV37_-AvyHHlAatqpbskZVgne5VWm7EiR6tal1jecH3JtzrFsHd8bYV0fo1d8Ym8hwUVzGhax0wKtQScg5pTBW0EARtSlcmqNdrdNqwBdcqNJQL5rGqfaiJJf5_XXuwXKY2SNMvoeNpER_HzjIkQRYchgDlMeuRkDYBclq834zFFRxeDP_s1kv2qDDpUDVEO", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c3a0000c54ce2f2_0%7C0a220b774c3d0000a9239654_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=Elcgh0lZk4w-Cd7QXTkVtquK4vphm8Ka7nrniw5pgkQDxaVcEJJc0NFg3Vb7MnGWhmW7iJuY2PFHinym0eQvAjgEpszA40SpExbaSkVfeUdMhgmKk2EeXf3xs9COuBBDbs86wIqINA5fwNGa0Aiex1UUMY8AGKpl_awGyE6Us60q9B6IoIN977F0jbD5_yqV50BQOkCqAdAehieynD1DAJWsEdk3s_DzCwgcjd5U5H8kfSN6gk1RnAXRzkpPpEwPgum8XUae-QX06NPT8mDFAC8702ILKYR7EhbgwFWZ6o-iorHIzbvziUVM81LvcWbNCCPAmRXWUyKZgd9b1bcS5n_jhc7nN6NWqeLy-z0bP3LQXqAkmNtpv4UjXO58wL_QW07PLuS5ohszs1eaBJ-ybl7c7EX3otx9wYSiPrB8opNt0GRHN6EQCa6d9hF4scnOkR2GSYv-_N82fMucTndPBtC-wO9V4PSyZ-vBT0Y2tmDe1tpQojX1p2SgccwBXd0pbAZ0xi3JtvoKAzABgI0eTUBhAurHnoL3yBNuGWJSspAcrBOnD8q2FaFYajZ0aHJSCoV37_-AvyHHlAatqpbskZVgne5VWm7EiR6tal1jecH3JtzrFsHd8bYV0fo1d8Ym8hwUVzGhax0wKtQScg5pTBW0EARtSlcmqNdrdNqwBdcqNJQL5rGqfaiJJf5_XXuwXKY2SNMvoeNpER_HzjIkQRYchgDlMeuRkDYBclq834zFFRxeDP_s1kv2qDDpUDVEO", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-06T10:15:00.000Z", "utc_arrival": "2023-06-06T08:15:00.000Z", "local_departure": "2023-06-06T06:55:00.000Z", "utc_departure": "2023-06-06T04:55:00.000Z"}, {"id": "0b770a224c1f00002a8dc654_0|0a220b774c23000067c13b26_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 758.193344, "distance": 1975.87, "duration": {"departure": 11700, "return": 11700, "total": 23400}, "price": 231569.9543, "conversion": {"EUR": 606.193724, "HUF": 231569.9543}, "fare": {"adults": 115784.98, "children": 115784.98, "infants": 115784.98}, "bags_price": {"1": 76.3, "2": 162.4}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 158, "hold_height": 52, "hold_length": 78, "hold_weight": 20, "hold_width": 28, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 3, "personal_item_width": 15}, "availability": {"seats": 3}, "airlines": ["W6", "IB"], "route": [{"id": "0b770a224c1f00002a8dc654_0", "combination_id": "0b770a224c1f00002a8dc654", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "IB", "flight_no": 3279, "operating_carrier": "IB", "operating_flight_no": "3279", "fare_basis": "NZNNAOB4", "fare_category": "M", "fare_classes": "N", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-10T18:50:00.000Z", "utc_arrival": "2023-05-10T16:50:00.000Z", "local_departure": "2023-05-10T15:35:00.000Z", "utc_departure": "2023-05-10T13:35:00.000Z"}, {"id": "0a220b774c23000067c13b26_0", "combination_id": "0a220b774c23000067c13b26", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IJREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-14T21:05:00.000Z", "utc_arrival": "2023-05-14T19:05:00.000Z", "local_departure": "2023-05-14T17:50:00.000Z", "utc_departure": "2023-05-14T15:50:00.000Z"}], "booking_token": "ERExzqnGe4sk2v1rkA86vADA4CAaM-w2rQBFlSemN8Z5ZVntg4zDqW5oFPQN9IENAQ90Zs1NSOxfC3iFsgd36Zczy2cT6YWS5qUdFjxMIWO08iCr4MwX9U17rzcnk3nbZ3xXz1qddy0x1ay_nVoKl2WAWxaDDVb35E0B7OQn52IXFwcg1QX1G70N4HLXCv4fFjZVT8fAi5CQzK23zFc-Lvcdc4vXo5DTbGpkonJO3Tjbk-Rr_cDwn8kG0GClf_8UC566q00umlse24-U5XTFFX-350-zWYqpQcDSb5l-elinc5TIdxqiQnrDeIteTrDyriYhjeddnVUu9hzcjdXDSCGHqF6W0pQ9mows-PVXXmDPX97t6OIdAqJQvavZitMdNI0U55tKkIErwVNlOMC5P0KnyvFCT68i3juuXATAgqsRQJ_0YNgN_C2cZ1wkVxS9lVcDgSxGC7JDQJ_WqOfTdKo-F_sOvdsI7G8s-ZF3z7URdb4EkGVfnRdI_23W-yz-BQb_M-tctZvaJDmkGXw_0cs54zamsQ5UNXczXc6-sUf8SYHRpu0QNCF-wck9as5XsDIWwEk_678XdHj21EfOfmcne4UdDbj9TWJfM-xDWtu59d_p0Sbb5QvSe9O79xZJ9gHV20AACa8ooVssv6a1GaDX0zMCWsfdQrt8EpIfDiUJG6_EWrJjeft58cxT3aDz5BRPbKopjq2mgJdqDNN0IK6yTT8RO-bt7ek5Di-Mt0wVKuMxyyIRkOZ_E8fWqmXdftF6R2bkXrSqGExUCYr2-r26sdMOlL1NLoOaVJ-qLuvA=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c1f00002a8dc654_0%7C0a220b774c23000067c13b26_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=ERExzqnGe4sk2v1rkA86vADA4CAaM-w2rQBFlSemN8Z5ZVntg4zDqW5oFPQN9IENAQ90Zs1NSOxfC3iFsgd36Zczy2cT6YWS5qUdFjxMIWO08iCr4MwX9U17rzcnk3nbZ3xXz1qddy0x1ay_nVoKl2WAWxaDDVb35E0B7OQn52IXFwcg1QX1G70N4HLXCv4fFjZVT8fAi5CQzK23zFc-Lvcdc4vXo5DTbGpkonJO3Tjbk-Rr_cDwn8kG0GClf_8UC566q00umlse24-U5XTFFX-350-zWYqpQcDSb5l-elinc5TIdxqiQnrDeIteTrDyriYhjeddnVUu9hzcjdXDSCGHqF6W0pQ9mows-PVXXmDPX97t6OIdAqJQvavZitMdNI0U55tKkIErwVNlOMC5P0KnyvFCT68i3juuXATAgqsRQJ_0YNgN_C2cZ1wkVxS9lVcDgSxGC7JDQJ_WqOfTdKo-F_sOvdsI7G8s-ZF3z7URdb4EkGVfnRdI_23W-yz-BQb_M-tctZvaJDmkGXw_0cs54zamsQ5UNXczXc6-sUf8SYHRpu0QNCF-wck9as5XsDIWwEk_678XdHj21EfOfmcne4UdDbj9TWJfM-xDWtu59d_p0Sbb5QvSe9O79xZJ9gHV20AACa8ooVssv6a1GaDX0zMCWsfdQrt8EpIfDiUJG6_EWrJjeft58cxT3aDz5BRPbKopjq2mgJdqDNN0IK6yTT8RO-bt7ek5Di-Mt0wVKuMxyyIRkOZ_E8fWqmXdftF6R2bkXrSqGExUCYr2-r26sdMOlL1NLoOaVJ-qLuvA=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-10T18:50:00.000Z", "utc_arrival": "2023-05-10T16:50:00.000Z", "local_departure": "2023-05-10T15:35:00.000Z", "utc_departure": "2023-05-10T13:35:00.000Z"}, {"id": "0b770a224c200000df962b2d_0|0a220b774c23000067c13b26_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 758.193344, "distance": 1975.87, "duration": {"departure": 11700, "return": 11700, "total": 23400}, "price": 231569.9543, "conversion": {"EUR": 606.193724, "HUF": 231569.9543}, "fare": {"adults": 115784.98, "children": 115784.98, "infants": 115784.98}, "bags_price": {"1": 76.3, "2": 162.4}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 158, "hold_height": 52, "hold_length": 78, "hold_weight": 20, "hold_width": 28, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 3, "personal_item_width": 15}, "availability": {"seats": 3}, "airlines": ["W6", "IB"], "route": [{"id": "0b770a224c200000df962b2d_0", "combination_id": "0b770a224c200000df962b2d", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "IB", "flight_no": 3279, "operating_carrier": "IB", "operating_flight_no": "3279", "fare_basis": "NZNNAOB4", "fare_category": "M", "fare_classes": "N", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-11T18:50:00.000Z", "utc_arrival": "2023-05-11T16:50:00.000Z", "local_departure": "2023-05-11T15:35:00.000Z", "utc_departure": "2023-05-11T13:35:00.000Z"}, {"id": "0a220b774c23000067c13b26_0", "combination_id": "0a220b774c23000067c13b26", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IJREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-14T21:05:00.000Z", "utc_arrival": "2023-05-14T19:05:00.000Z", "local_departure": "2023-05-14T17:50:00.000Z", "utc_departure": "2023-05-14T15:50:00.000Z"}], "booking_token": "Eeeu3_-GTae9WINtBnPJcnrLcsz_sc2xGQk5RhXxbTT8s8s9NBIsKZ2Lf9UQfcC5sYN_DlFxNOoNk-c94cvj4eNQHwse1sFKDPOHvqgJZOAyR3V5xY4GmWdUca-SaTjSj79Pd0Oh_wNDpxgjtbtmNFV9xIhBWwgHtSRRBUtiuwt8HQB9LMXwelvqj5spj8djS2GIosXMJXuWUKvfMz6zHvR6stUSpCdHI_ES7nAfKGVoA59RPejrNsk4_LSt8ZwG5g9h6akUEFMyrxX1eIkWfQryDSYBcrEQjMkwgxggL6Ap4KTAct2u_HrLrvHXXJDgeHMoeSW9BlxvsWAQpBp_dVd2cCTbQRDU847QoEgP-2yTx7Tde0e7efuqtKMfB3JOizeSv7ELkSocuB6_2gIM40HsyDsNQ8ZoZrbnqYNAD_wTTKrpFO4Q6qUWIA7Zztg2cr0eJRMyjsFCWhgDCt-j_blDa6NakXs1xnF-ZKD1e9z04oBBbWWeBi6SML6Onp5UjA4zI1brNbo7S-UNqf3OwJHiP3tnW-qg5pzvPZOSqWJJfJiDDUoF31wOIlD6zJ3MK-HmwIpIMp35NSsO7ZDANKqHZIoKcaEz4zbR0nu1Tbqg_IVXyP8pXE9Z9x18xgxUtgctpsnx_iBhk43q5-qZN20B_oFuOVnURv_WmBxzLvf1dKPhd1c3PQNhqvl38J1TP0c6vVB4oixb5ljtrMJKmw-X0FRN1T7eMEmRUeG2ieWswSVl5n4vg3hnEE9KbppaR0myyeHV9vRIa7ndoBABtoJy0kqw8ylJAWX2COKSP6IE=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c200000df962b2d_0%7C0a220b774c23000067c13b26_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=Eeeu3_-GTae9WINtBnPJcnrLcsz_sc2xGQk5RhXxbTT8s8s9NBIsKZ2Lf9UQfcC5sYN_DlFxNOoNk-c94cvj4eNQHwse1sFKDPOHvqgJZOAyR3V5xY4GmWdUca-SaTjSj79Pd0Oh_wNDpxgjtbtmNFV9xIhBWwgHtSRRBUtiuwt8HQB9LMXwelvqj5spj8djS2GIosXMJXuWUKvfMz6zHvR6stUSpCdHI_ES7nAfKGVoA59RPejrNsk4_LSt8ZwG5g9h6akUEFMyrxX1eIkWfQryDSYBcrEQjMkwgxggL6Ap4KTAct2u_HrLrvHXXJDgeHMoeSW9BlxvsWAQpBp_dVd2cCTbQRDU847QoEgP-2yTx7Tde0e7efuqtKMfB3JOizeSv7ELkSocuB6_2gIM40HsyDsNQ8ZoZrbnqYNAD_wTTKrpFO4Q6qUWIA7Zztg2cr0eJRMyjsFCWhgDCt-j_blDa6NakXs1xnF-ZKD1e9z04oBBbWWeBi6SML6Onp5UjA4zI1brNbo7S-UNqf3OwJHiP3tnW-qg5pzvPZOSqWJJfJiDDUoF31wOIlD6zJ3MK-HmwIpIMp35NSsO7ZDANKqHZIoKcaEz4zbR0nu1Tbqg_IVXyP8pXE9Z9x18xgxUtgctpsnx_iBhk43q5-qZN20B_oFuOVnURv_WmBxzLvf1dKPhd1c3PQNhqvl38J1TP0c6vVB4oixb5ljtrMJKmw-X0FRN1T7eMEmRUeG2ieWswSVl5n4vg3hnEE9KbppaR0myyeHV9vRIa7ndoBABtoJy0kqw8ylJAWX2COKSP6IE=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-11T18:50:00.000Z", "utc_arrival": "2023-05-11T16:50:00.000Z", "local_departure": "2023-05-11T15:35:00.000Z", "utc_departure": "2023-05-11T13:35:00.000Z"}, {"id": "0b770a224c34000076b49bc7_0|0a220b774c370000e3d9a22a_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 757.324222, "distance": 1975.87, "duration": {"departure": 11700, "return": 11400, "total": 23100}, "price": 231747.2848, "conversion": {"EUR": 606.657932, "HUF": 231747.2848}, "fare": {"adults": 115873.64, "children": 115873.64, "infants": 115873.64}, "bags_price": {"1": 74.186, "2": 158.172}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 158, "hold_height": 52, "hold_length": 78, "hold_weight": 20, "hold_width": 28, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 3, "personal_item_width": 15}, "availability": {"seats": 6}, "airlines": ["FR", "IB"], "route": [{"id": "0b770a224c34000076b49bc7_0", "combination_id": "0b770a224c34000076b49bc7", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "IB", "flight_no": 3279, "operating_carrier": "IB", "operating_flight_no": "3279", "fare_basis": "NDNNAOB4", "fare_category": "M", "fare_classes": "N", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-31T18:50:00.000Z", "utc_arrival": "2023-05-31T16:50:00.000Z", "local_departure": "2023-05-31T15:35:00.000Z", "utc_departure": "2023-05-31T13:35:00.000Z"}, {"id": "0a220b774c370000e3d9a22a_0", "combination_id": "0a220b774c370000e3d9a22a", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-03T09:40:00.000Z", "utc_arrival": "2023-06-03T07:40:00.000Z", "local_departure": "2023-06-03T06:30:00.000Z", "utc_departure": "2023-06-03T04:30:00.000Z"}], "booking_token": "E5Fy1iR1vWAcScPr2Nj-HdpAQaMgC03JiN26EMu2eZ9pbbVwEFd4OeR3M3rNi_aUEOd3wjNMUZ0mDoEFx6rIFJk6PkBTw0R-43Fi7-uk_IBxNLKvNNmEoRt_VwXsBX8F8Daj7KZ4rWpD2LoPPC-UZEHMn3_yereZRcf90ir2Dz4SI7elot18n0pDKHtuR5HcltP8fJiQ0axkzGgVvrno7dNuPAFLvXYOVUBvSqf3JYzzWnm9ltrMz7hlWI4IU4xVdgt5jZa-iDGFI4iYwbDfjPQsKyKdGTTcpl5oH0pt0E6r5r_3suLa08e9akpPfG_L6t8P2Ld5XgF_r8d0bTMYIGJXN4BUMpMqBXG0BreI4L43MydPnEr_S8mr8BBYPOevT6AS7QswkNw4kuZdvJKG7xneqz4ffY0wEIs2StgWeL9UE7AHm_TnbitYXFMk9e0kUUTP4X6lOava9QcJ9bC5B-2OWqUCJffdrAeGCYfehqNQJ6ge7tBNnofzVHtFz3QUHyR0dy6Nprxn675n5h62Hp86WMSuu3TlY4Z_CRjXMj4phjnalOXSacPuG9wxjZM67rD61BQb7C4QiwWD08Ol_BdpiIEDsju1JiqWVimcygwot1n1m4VhE068PQ3EJhVENbbvHeMC0YA7yDaNGCXOKhrzjiK5nVgD3BGi5za5ghdKPXyrV2R02X6cJKcjXm3svCjAsmrqJWxGtvFhSg1dh0ZWtGcPxZ_A3v5sE8f8jxGBwe31mvvHFgdY_2Nkr9B0a69QHo9k3KxAge63mSqZJXXT9XnXnvXndmCgpLPZpFGU=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c34000076b49bc7_0%7C0a220b774c370000e3d9a22a_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=E5Fy1iR1vWAcScPr2Nj-HdpAQaMgC03JiN26EMu2eZ9pbbVwEFd4OeR3M3rNi_aUEOd3wjNMUZ0mDoEFx6rIFJk6PkBTw0R-43Fi7-uk_IBxNLKvNNmEoRt_VwXsBX8F8Daj7KZ4rWpD2LoPPC-UZEHMn3_yereZRcf90ir2Dz4SI7elot18n0pDKHtuR5HcltP8fJiQ0axkzGgVvrno7dNuPAFLvXYOVUBvSqf3JYzzWnm9ltrMz7hlWI4IU4xVdgt5jZa-iDGFI4iYwbDfjPQsKyKdGTTcpl5oH0pt0E6r5r_3suLa08e9akpPfG_L6t8P2Ld5XgF_r8d0bTMYIGJXN4BUMpMqBXG0BreI4L43MydPnEr_S8mr8BBYPOevT6AS7QswkNw4kuZdvJKG7xneqz4ffY0wEIs2StgWeL9UE7AHm_TnbitYXFMk9e0kUUTP4X6lOava9QcJ9bC5B-2OWqUCJffdrAeGCYfehqNQJ6ge7tBNnofzVHtFz3QUHyR0dy6Nprxn675n5h62Hp86WMSuu3TlY4Z_CRjXMj4phjnalOXSacPuG9wxjZM67rD61BQb7C4QiwWD08Ol_BdpiIEDsju1JiqWVimcygwot1n1m4VhE068PQ3EJhVENbbvHeMC0YA7yDaNGCXOKhrzjiK5nVgD3BGi5za5ghdKPXyrV2R02X6cJKcjXm3svCjAsmrqJWxGtvFhSg1dh0ZWtGcPxZ_A3v5sE8f8jxGBwe31mvvHFgdY_2Nkr9B0a69QHo9k3KxAge63mSqZJXXT9XnXnvXndmCgpLPZpFGU=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-31T18:50:00.000Z", "utc_arrival": "2023-05-31T16:50:00.000Z", "local_departure": "2023-05-31T15:35:00.000Z", "utc_departure": "2023-05-31T13:35:00.000Z"}, {"id": "0b770a224c470000f72dd482_0|0a220b774c4b0000d381db8e_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 762.978604, "distance": 1975.87, "duration": {"departure": 12600, "return": 11700, "total": 24300}, "price": 231869.9326, "conversion": {"EUR": 606.978994, "HUF": 231869.9326}, "fare": {"adults": 115934.97, "children": 115934.97, "infants": 115934.97}, "bags_price": {"1": 118.832, "2": 237.678}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 439, "hold_height": 149, "hold_length": 171, "hold_weight": 20, "hold_width": 119, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 2}, "airlines": ["W6"], "route": [{"id": "0b770a224c470000f72dd482_0", "combination_id": "0b770a224c470000f72dd482", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-19T19:45:00.000Z", "utc_arrival": "2023-06-19T17:45:00.000Z", "local_departure": "2023-06-19T16:15:00.000Z", "utc_departure": "2023-06-19T14:15:00.000Z"}, {"id": "0a220b774c4b0000d381db8e_0", "combination_id": "0a220b774c4b0000d381db8e", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "JREG", "fare_category": "M", "fare_classes": "J", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-23T23:45:00.000Z", "utc_arrival": "2023-06-23T21:45:00.000Z", "local_departure": "2023-06-23T20:30:00.000Z", "utc_departure": "2023-06-23T18:30:00.000Z"}], "booking_token": "EtTVg4qvGj5TqlLSo7kHHRYUCLvOvEdDhJuXiaC1PF8nrRLMresyuxGnqLLelXGmbtRxvdPeAqqjQ2wDSgCsku2IuoeascphtdyHEseaG8jxCSGYsY_mZj9Ww1JHGQ2-p3kW6upWsIrvXHphggUw6VEG6tKHaR2DOaZU8VXi5aGRh34-9_6k_Fjpi6VmE51NcU-K81T7LWWIbaSoIN0Sm9yBktQDXtS9_nDU5eV7dqmwWMmyIUZZRZXUMPbM19Kihh6ITw7LzX-S424LGnhipomTnI3XThY-oR7ly22IdR-WBuTdEw8K7mrDoDeHV6IzdVdSjFaHVMIbGzWbCW0eC1zr3i6vQzgNmIz0Vm23Yp65CXbPKlRQhtiyNownrB0CGkOV_Z8fRg7RgtBdSLgutiZHXFC9o37XWefDj6Bd9cr_NJVTrmh-iLGPO7i3hKx3zxKmo4gQJzkvAq04bfKgUXvCPF9zTp8DefAfLOW2jeZJ0iUfROB0qiw1p-xZIp6dUET0H7l9hIVmMhojySS_W9sJg8jGq6E7MxNxlr_QNmd9ZDEf2WodNPghnbQ5TCz3bool0I22KV3A7wTFBQe8Qb8uhsz_6T1LqdFtkvKEcDQaUZnNDmb_kHvKyI_4M_u8ovgum4yuzp0QuMuj6GTctDkS0M_K4Rt4HjBlmGXUB4W0D__LFRTs09e661O8XlnZd2ah06WrT42CwHqjnN42W1mGuSX1Lkp2t3cH2KpcNSRBY5jKh9mRCc5gQBT8j3YMdFrFh8JpEPBUS1K5VFe0RgMt7Bph3RK6Jg7Rz5eLIk4A=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c470000f72dd482_0%7C0a220b774c4b0000d381db8e_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EtTVg4qvGj5TqlLSo7kHHRYUCLvOvEdDhJuXiaC1PF8nrRLMresyuxGnqLLelXGmbtRxvdPeAqqjQ2wDSgCsku2IuoeascphtdyHEseaG8jxCSGYsY_mZj9Ww1JHGQ2-p3kW6upWsIrvXHphggUw6VEG6tKHaR2DOaZU8VXi5aGRh34-9_6k_Fjpi6VmE51NcU-K81T7LWWIbaSoIN0Sm9yBktQDXtS9_nDU5eV7dqmwWMmyIUZZRZXUMPbM19Kihh6ITw7LzX-S424LGnhipomTnI3XThY-oR7ly22IdR-WBuTdEw8K7mrDoDeHV6IzdVdSjFaHVMIbGzWbCW0eC1zr3i6vQzgNmIz0Vm23Yp65CXbPKlRQhtiyNownrB0CGkOV_Z8fRg7RgtBdSLgutiZHXFC9o37XWefDj6Bd9cr_NJVTrmh-iLGPO7i3hKx3zxKmo4gQJzkvAq04bfKgUXvCPF9zTp8DefAfLOW2jeZJ0iUfROB0qiw1p-xZIp6dUET0H7l9hIVmMhojySS_W9sJg8jGq6E7MxNxlr_QNmd9ZDEf2WodNPghnbQ5TCz3bool0I22KV3A7wTFBQe8Qb8uhsz_6T1LqdFtkvKEcDQaUZnNDmb_kHvKyI_4M_u8ovgum4yuzp0QuMuj6GTctDkS0M_K4Rt4HjBlmGXUB4W0D__LFRTs09e661O8XlnZd2ah06WrT42CwHqjnN42W1mGuSX1Lkp2t3cH2KpcNSRBY5jKh9mRCc5gQBT8j3YMdFrFh8JpEPBUS1K5VFe0RgMt7Bph3RK6Jg7Rz5eLIk4A=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-19T19:45:00.000Z", "utc_arrival": "2023-06-19T17:45:00.000Z", "local_departure": "2023-06-19T16:15:00.000Z", "utc_departure": "2023-06-19T14:15:00.000Z"}, {"id": "0b770a224c470000f72dd482_0|0a220b774c4a0000f5177ada_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 762.978604, "distance": 1975.87, "duration": {"departure": 12600, "return": 11700, "total": 24300}, "price": 231869.9326, "conversion": {"EUR": 606.978994, "HUF": 231869.9326}, "fare": {"adults": 115934.97, "children": 115934.97, "infants": 115934.97}, "bags_price": {"1": 118.832, "2": 237.678}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 439, "hold_height": 149, "hold_length": 171, "hold_weight": 20, "hold_width": 119, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 5}, "airlines": ["W6"], "route": [{"id": "0b770a224c470000f72dd482_0", "combination_id": "0b770a224c470000f72dd482", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-19T19:45:00.000Z", "utc_arrival": "2023-06-19T17:45:00.000Z", "local_departure": "2023-06-19T16:15:00.000Z", "utc_departure": "2023-06-19T14:15:00.000Z"}, {"id": "0a220b774c4a0000f5177ada_0", "combination_id": "0a220b774c4a0000f5177ada", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "JREG", "fare_category": "M", "fare_classes": "J", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-23T01:15:00.000Z", "utc_arrival": "2023-06-22T23:15:00.000Z", "local_departure": "2023-06-22T22:00:00.000Z", "utc_departure": "2023-06-22T20:00:00.000Z"}], "booking_token": "EMYOST0EFhEAZpPdw2jse0X_aJMfPtQbNpieOsLGT99FUKlW3GQ6xWlL4QTl3PLVR6muTC6R_f64S7QQR6DVf0li9_QJjzbq_PmYfOLLSuNEMYBQjVByJ1PDneWS3PVcLo-HyKrU_sR7yVc3mTLo2JFz4IZhtuPuD41__FWo9QM5ZE42k_vyVTuh3vKJa64IdmYVGlZSIYAKWJG9do85N1c0ROpAz7TekOahIePFlZr1zckOHdI8reU-g8KV-_USFICrnwcgxzCo_PYq2o5GgQGtuHIzXnH-6rY_DU2lo95osBj8klybrCwqzHB9h3dASsJB2xFJx-xUeylC4TYa_rBG5Ufs3TvimiGkmjXfPb5Wz_D0WvPo1lyW8sVY0szLm01AT2ZtgSZhGnt4Aaek2HWFuKhIrPjZ7kCbGabHnpye8GDQIPKy7DTpGY3iG0cx9FoqfIk0s_W2nfL8X28eR9H7WVmEisMw_WBmbaNB5ILfsVO1Ss1A5thCxQeEVSLEQFhuLcIWP2RZdY2dqpbZ3b2pl8AWDyUJ_zQErFVnQSCZ6KRp-8i7Hp-ndBAKmTYLU1hkRoEn_xHnFByTL0MzX5eqvo_CTa5dMwXEKWEmWKdyXfe8nyE1emYVj1cuEoCLYBA9iEAFO_yedDqDZ6fdhvudfhM_DkB_zR_-ofMERVl0YKd0T-mX-5yKtHVHQUVJHMbZ0acYWeraORei73UiysUhuY902KSFXR9Y0V4BnBGeQaF9YRzx4tzOCIUtKoSyGHFxGemR_AHBe0WjAUuEiGgHar8VE3lfApYOLASfpcNg=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c470000f72dd482_0%7C0a220b774c4a0000f5177ada_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EMYOST0EFhEAZpPdw2jse0X_aJMfPtQbNpieOsLGT99FUKlW3GQ6xWlL4QTl3PLVR6muTC6R_f64S7QQR6DVf0li9_QJjzbq_PmYfOLLSuNEMYBQjVByJ1PDneWS3PVcLo-HyKrU_sR7yVc3mTLo2JFz4IZhtuPuD41__FWo9QM5ZE42k_vyVTuh3vKJa64IdmYVGlZSIYAKWJG9do85N1c0ROpAz7TekOahIePFlZr1zckOHdI8reU-g8KV-_USFICrnwcgxzCo_PYq2o5GgQGtuHIzXnH-6rY_DU2lo95osBj8klybrCwqzHB9h3dASsJB2xFJx-xUeylC4TYa_rBG5Ufs3TvimiGkmjXfPb5Wz_D0WvPo1lyW8sVY0szLm01AT2ZtgSZhGnt4Aaek2HWFuKhIrPjZ7kCbGabHnpye8GDQIPKy7DTpGY3iG0cx9FoqfIk0s_W2nfL8X28eR9H7WVmEisMw_WBmbaNB5ILfsVO1Ss1A5thCxQeEVSLEQFhuLcIWP2RZdY2dqpbZ3b2pl8AWDyUJ_zQErFVnQSCZ6KRp-8i7Hp-ndBAKmTYLU1hkRoEn_xHnFByTL0MzX5eqvo_CTa5dMwXEKWEmWKdyXfe8nyE1emYVj1cuEoCLYBA9iEAFO_yedDqDZ6fdhvudfhM_DkB_zR_-ofMERVl0YKd0T-mX-5yKtHVHQUVJHMbZ0acYWeraORei73UiysUhuY902KSFXR9Y0V4BnBGeQaF9YRzx4tzOCIUtKoSyGHFxGemR_AHBe0WjAUuEiGgHar8VE3lfApYOLASfpcNg=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-19T19:45:00.000Z", "utc_arrival": "2023-06-19T17:45:00.000Z", "local_departure": "2023-06-19T16:15:00.000Z", "utc_departure": "2023-06-19T14:15:00.000Z"}, {"id": "0b770a224c060000e57211e2_0|0a220b774c090000137a3e18_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 759.25173, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 231974.2647, "conversion": {"EUR": 607.25211, "HUF": 231974.2647}, "fare": {"adults": 115987.13, "children": 115987.13, "infants": 115987.13}, "bags_price": {"1": 97.972, "2": 195.944}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 5}, "airlines": ["FR"], "route": [{"id": "0b770a224c060000e57211e2_0", "combination_id": "0b770a224c060000e57211e2", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-15T13:25:00.000Z", "utc_arrival": "2023-04-15T11:25:00.000Z", "local_departure": "2023-04-15T10:05:00.000Z", "utc_departure": "2023-04-15T08:05:00.000Z"}, {"id": "0a220b774c090000137a3e18_0", "combination_id": "0a220b774c090000137a3e18", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-18T14:05:00.000Z", "utc_arrival": "2023-04-18T12:05:00.000Z", "local_departure": "2023-04-18T10:55:00.000Z", "utc_departure": "2023-04-18T08:55:00.000Z"}], "booking_token": "EZJ6svixsxxOzW-Bi-nCU5NvVXomZViVwsAjKOKfys2TQSqYa6vQt5WJ4Ow_fK7PKRBNHWYLQreZbEh5vAqFSrdNHErP-LSXmgYYvOcKzotGSii8JlIr56CaH69FUe5zc8yRxnJSeTe9QcDrU2z6nRqIX2USSleJLyCG0ekpz9xZPBVatcfOABmBXjaqFJmKxQfD3OHJLkvRrPy2w9l-sKIA8hwPwfohMT1ee2CvYhlKA1THGu1BlmGTBD_eiPqbzXHem2c3O9LKnPsVFO4ge5040DBSeLUnumqQNtkrAQn5SF03SXiXJuSGyUQJU8-TOf25CMgejOjccyokUIW18VzfjYug9p760SnGIGWDEW6LIuxV247N4SJwzu25Sn6mRsRGPxGOkVIH36wLVCZO3TmXGZzJYQjwMVs1lTGHw3l0UcW5p11_kQAT6tFWkP0NO_fxXShiKSTv8X0fB1svSnYYerxnwPD-nFIoiXiipZKmyCsw0jwuXcxaWL9Qv54KmuL-G5hdU6blj9ZRXOufH1I-isdjB5jKlMswOKqI4t-fUU_Ug4aGa69lZZQBGoz02pPwFzyaANmfdex2D4jX5MML5Kx0EIIWBN44FYhb7w6Z-Z2Oqzvr8TpT8nKDis91hYmInZeLNi85HFslKOQxgpQLdmn0LBGkWxcg-iXbntesuWDRV2UiAiTybWpo5FzkjvhdDmnc3ctyineRtf-d-Ae63A7rEmijtKo631bwoNSkcNC0cNGWA5fi6k1q4E1YZ", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c060000e57211e2_0%7C0a220b774c090000137a3e18_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EZJ6svixsxxOzW-Bi-nCU5NvVXomZViVwsAjKOKfys2TQSqYa6vQt5WJ4Ow_fK7PKRBNHWYLQreZbEh5vAqFSrdNHErP-LSXmgYYvOcKzotGSii8JlIr56CaH69FUe5zc8yRxnJSeTe9QcDrU2z6nRqIX2USSleJLyCG0ekpz9xZPBVatcfOABmBXjaqFJmKxQfD3OHJLkvRrPy2w9l-sKIA8hwPwfohMT1ee2CvYhlKA1THGu1BlmGTBD_eiPqbzXHem2c3O9LKnPsVFO4ge5040DBSeLUnumqQNtkrAQn5SF03SXiXJuSGyUQJU8-TOf25CMgejOjccyokUIW18VzfjYug9p760SnGIGWDEW6LIuxV247N4SJwzu25Sn6mRsRGPxGOkVIH36wLVCZO3TmXGZzJYQjwMVs1lTGHw3l0UcW5p11_kQAT6tFWkP0NO_fxXShiKSTv8X0fB1svSnYYerxnwPD-nFIoiXiipZKmyCsw0jwuXcxaWL9Qv54KmuL-G5hdU6blj9ZRXOufH1I-isdjB5jKlMswOKqI4t-fUU_Ug4aGa69lZZQBGoz02pPwFzyaANmfdex2D4jX5MML5Kx0EIIWBN44FYhb7w6Z-Z2Oqzvr8TpT8nKDis91hYmInZeLNi85HFslKOQxgpQLdmn0LBGkWxcg-iXbntesuWDRV2UiAiTybWpo5FzkjvhdDmnc3ctyineRtf-d-Ae63A7rEmijtKo631bwoNSkcNC0cNGWA5fi6k1q4E1YZ", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-04-15T13:25:00.000Z", "utc_arrival": "2023-04-15T11:25:00.000Z", "local_departure": "2023-04-15T10:05:00.000Z", "utc_departure": "2023-04-15T08:05:00.000Z"}, {"id": "0b770a224c430000a78af0de_0|0a220b774c47000069bc4867_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 763.41371, "distance": 1975.87, "duration": {"departure": 12600, "return": 11700, "total": 24300}, "price": 232036.1459, "conversion": {"EUR": 607.4141, "HUF": 232036.1459}, "fare": {"adults": 116018.07, "children": 116018.07, "infants": 116018.07}, "bags_price": {"1": 90.986, "2": 181.972}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 439, "hold_height": 149, "hold_length": 171, "hold_weight": 20, "hold_width": 119, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 2}, "airlines": ["W6"], "route": [{"id": "0b770a224c430000a78af0de_0", "combination_id": "0b770a224c430000a78af0de", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IJREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-15T21:15:00.000Z", "utc_arrival": "2023-06-15T19:15:00.000Z", "local_departure": "2023-06-15T17:45:00.000Z", "utc_departure": "2023-06-15T15:45:00.000Z"}, {"id": "0a220b774c47000069bc4867_0", "combination_id": "0a220b774c47000069bc4867", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-19T23:45:00.000Z", "utc_arrival": "2023-06-19T21:45:00.000Z", "local_departure": "2023-06-19T20:30:00.000Z", "utc_departure": "2023-06-19T18:30:00.000Z"}], "booking_token": "Et2Imh83I9DBSC_TQz9xhEV9zd9ZzoDltQThInvXWe2onBDeQhov9cCac99FdhlbYhB8WB35OnWp9Bxq45Brgajc1YEOJwUXa16UNwZFNJEHUbYkUGVg4NKxGd4PjL1b4pmwPRPaR1r38aVIu83Sj7Mh9uAU1AzklWnAec4-t_zAerQhL_GP9oFeGDceFn-fsOjdeFrfIAZ04d2LDXuTcs0cXl0cKwytmR12RUsQmLKkeuDIDqawkxvGDoQGa-180HfV-ocfzUXdmMWDSUuutUGRf3s7JiWaocTK4Bt6xqojTnSxl2qLMxiwNiUeitx8D9pfnmfU40bEHePOlERO-vx6Vb0vjDaJ_IWdK4boZtd0rZwW21Fxio04qBWwTxco2F6gFH0gjJpkOXthYWdLqqmlVtwM3QhaCb5R6dwV9ahQHeaM30G4ME3uGrSqRBs-0wvLzBk8RCQXVTDFLHlmgL0PF5bq3zRT5FBaOAnlobbKKz_-5lEpzgeAKlD0gao89eAlvhuof1Hame2tUlD4uSbk9pvs3SR3cH-Pe4Nbwvhlj7EBqVWwaPSxeJa9HekKJRaGzL3kjSp2BP6otEYiRaUxxpfVzVy9jzplxB33NoX9KLi9bK2lCRPR4iAi4dSJxyOEQELL12tHGcx7PIqxwauCjm3V0lHBCLLwviu-Bf_d2LxEmk3NpA0inzfLPdNJdtkQGoZ3_EzEIv0fKiTC14WjWoGLW5G_geXvYzdgj90UZ8HH8K8YKEZC3Oa_OQQ9i", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c430000a78af0de_0%7C0a220b774c47000069bc4867_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=Et2Imh83I9DBSC_TQz9xhEV9zd9ZzoDltQThInvXWe2onBDeQhov9cCac99FdhlbYhB8WB35OnWp9Bxq45Brgajc1YEOJwUXa16UNwZFNJEHUbYkUGVg4NKxGd4PjL1b4pmwPRPaR1r38aVIu83Sj7Mh9uAU1AzklWnAec4-t_zAerQhL_GP9oFeGDceFn-fsOjdeFrfIAZ04d2LDXuTcs0cXl0cKwytmR12RUsQmLKkeuDIDqawkxvGDoQGa-180HfV-ocfzUXdmMWDSUuutUGRf3s7JiWaocTK4Bt6xqojTnSxl2qLMxiwNiUeitx8D9pfnmfU40bEHePOlERO-vx6Vb0vjDaJ_IWdK4boZtd0rZwW21Fxio04qBWwTxco2F6gFH0gjJpkOXthYWdLqqmlVtwM3QhaCb5R6dwV9ahQHeaM30G4ME3uGrSqRBs-0wvLzBk8RCQXVTDFLHlmgL0PF5bq3zRT5FBaOAnlobbKKz_-5lEpzgeAKlD0gao89eAlvhuof1Hame2tUlD4uSbk9pvs3SR3cH-Pe4Nbwvhlj7EBqVWwaPSxeJa9HekKJRaGzL3kjSp2BP6otEYiRaUxxpfVzVy9jzplxB33NoX9KLi9bK2lCRPR4iAi4dSJxyOEQELL12tHGcx7PIqxwauCjm3V0lHBCLLwviu-Bf_d2LxEmk3NpA0inzfLPdNJdtkQGoZ3_EzEIv0fKiTC14WjWoGLW5G_geXvYzdgj90UZ8HH8K8YKEZC3Oa_OQQ9i", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-15T21:15:00.000Z", "utc_arrival": "2023-06-15T19:15:00.000Z", "local_departure": "2023-06-15T17:45:00.000Z", "utc_departure": "2023-06-15T15:45:00.000Z"}, {"id": "0b770a224c494c4c2c61f31a_0|0b770a224c494c4c2c61f31a_1", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 759.114022, "distance": 1975.87, "duration": {"departure": 11700, "return": 11400, "total": 23100}, "price": 232431.0001, "conversion": {"EUR": 608.447732, "HUF": 232431.0001}, "fare": {"adults": 116215.5, "children": 116215.5, "infants": 116215.5}, "bags_price": {"1": 78.4, "2": 176.4}, "baglimit": {"hand_height": 40, "hand_length": 56, "hand_weight": 10, "hand_width": 25, "hold_dimensions_sum": 158, "hold_height": 52, "hold_length": 78, "hold_weight": 23, "hold_width": 28, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 3, "personal_item_width": 15}, "availability": {"seats": null}, "airlines": ["IB"], "route": [{"id": "0b770a224c494c4c2c61f31a_0", "combination_id": "0b770a224c494c4c2c61f31a", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "IB", "flight_no": 3279, "operating_carrier": "IB", "operating_flight_no": "3279", "fare_basis": "QDNNANB4", "fare_category": "M", "fare_classes": "Q", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-21T18:50:00.000Z", "utc_arrival": "2023-06-21T16:50:00.000Z", "local_departure": "2023-06-21T15:35:00.000Z", "utc_departure": "2023-06-21T13:35:00.000Z"}, {"id": "0b770a224c494c4c2c61f31a_1", "combination_id": "0b770a224c494c4c2c61f31a", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "IB", "flight_no": 3278, "operating_carrier": "IB", "operating_flight_no": "3278", "fare_basis": "NDNNANB4", "fare_category": "M", "fare_classes": "N", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-24T14:55:00.000Z", "utc_arrival": "2023-06-24T12:55:00.000Z", "local_departure": "2023-06-24T11:45:00.000Z", "utc_departure": "2023-06-24T09:45:00.000Z"}], "booking_token": "E9m-91Lw1N7Xi0-rxUkGU8_GemyS1euqHJx0V5atc70ubvf5dqGqx2CrcSSefzNGzEnaaXP0t0Ve5V17VsNmUpUI_hpBqWBP6vLWW0VT0iNy7Crj2D6XR5UfNk7B95uGmSpNE0mK8C1qjdjxzbeA6LWvOKr4GBlRmZfvtmhquKIEFbB49rD_PcTt9ptym9rEf-jKifMS-VTUOnqvPl4Wbj3ofzkr1mm89xSVH4b8cqFzixg0OeK_mkqIkl7DCKSGGtXNZWsiheddM2lOyIEKcU_9zk4JXdHYiUOZGWEMCs6JUpxtzwE6cBfeR4xcYQC-D1ajWI69GO2TsheI3d-J8hL0L7vUXblwfgste_H77eJIqPVmmSsisEiTKbqzQjQBh4MmkYXKSdS2XetVGs3O1QTNdQhY8rjVAWEpc_rdUibHlg7Exv3D4qkVZxROe2FKiCCzfrepcLD4kVAmTCWrcxZFSYsH6C3WDlKwM7LOLDo1GA0t78mWlbXbj1AQ3TIX2sakMLEX_I4CVQK341E_KtmgfvqSVRQYWtFBhKwbGxIODtFQbUooQUeNdBQsOj8WqgrWXtxkneImVxTJXcZbg0pUcVKyY9j45coCAhOmshwLr1T_1xYzsTWYttgF9LK2rNzQvA1-Q3Qo5O2C5hT4loBMx2NL6_hNcd8vQwlr-jYxhBnDKN9OOAxi6482AbbDv", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c494c4c2c61f31a_0%7C0b770a224c494c4c2c61f31a_1&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=E9m-91Lw1N7Xi0-rxUkGU8_GemyS1euqHJx0V5atc70ubvf5dqGqx2CrcSSefzNGzEnaaXP0t0Ve5V17VsNmUpUI_hpBqWBP6vLWW0VT0iNy7Crj2D6XR5UfNk7B95uGmSpNE0mK8C1qjdjxzbeA6LWvOKr4GBlRmZfvtmhquKIEFbB49rD_PcTt9ptym9rEf-jKifMS-VTUOnqvPl4Wbj3ofzkr1mm89xSVH4b8cqFzixg0OeK_mkqIkl7DCKSGGtXNZWsiheddM2lOyIEKcU_9zk4JXdHYiUOZGWEMCs6JUpxtzwE6cBfeR4xcYQC-D1ajWI69GO2TsheI3d-J8hL0L7vUXblwfgste_H77eJIqPVmmSsisEiTKbqzQjQBh4MmkYXKSdS2XetVGs3O1QTNdQhY8rjVAWEpc_rdUibHlg7Exv3D4qkVZxROe2FKiCCzfrepcLD4kVAmTCWrcxZFSYsH6C3WDlKwM7LOLDo1GA0t78mWlbXbj1AQ3TIX2sakMLEX_I4CVQK341E_KtmgfvqSVRQYWtFBhKwbGxIODtFQbUooQUeNdBQsOj8WqgrWXtxkneImVxTJXcZbg0pUcVKyY9j45coCAhOmshwLr1T_1xYzsTWYttgF9LK2rNzQvA1-Q3Qo5O2C5hT4loBMx2NL6_hNcd8vQwlr-jYxhBnDKN9OOAxi6482AbbDv", "facilitated_booking_available": true, "pnr_count": 1, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-21T18:50:00.000Z", "utc_arrival": "2023-06-21T16:50:00.000Z", "local_departure": "2023-06-21T15:35:00.000Z", "utc_departure": "2023-06-21T13:35:00.000Z"}, {"id": "0b770a224c09000063e5c3d1_0|0a220b774c0c0000c53091b6_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 768.51394, "distance": 1975.87, "duration": {"departure": 12000, "return": 12900, "total": 24900}, "price": 232965.7855, "conversion": {"EUR": 609.84767, "HUF": 232965.7855}, "fare": {"adults": 116482.89, "children": 119726.82, "infants": 119726.82}, "bags_price": {"1": 91.84, "2": 183.68}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 6}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224c09000063e5c3d1_0", "combination_id": "0b770a224c09000063e5c3d1", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-18T10:15:00.000Z", "utc_arrival": "2023-04-18T08:15:00.000Z", "local_departure": "2023-04-18T06:55:00.000Z", "utc_departure": "2023-04-18T04:55:00.000Z"}, {"id": "0a220b774c0c0000c53091b6_0", "combination_id": "0a220b774c0c0000c53091b6", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IJREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-22T00:05:00.000Z", "utc_arrival": "2023-04-21T22:05:00.000Z", "local_departure": "2023-04-21T20:30:00.000Z", "utc_departure": "2023-04-21T18:30:00.000Z"}], "booking_token": "E_g2qqSgt7-QIQeu7EkfIg3uxxS90OZwENsWd1Go-bgd9OttEVYeHfVePNP2h5YXN2x-wZowbpoZ_8w1L5hbYm8Snevts7qvx646eh4GGi-83eKUT_sqdWr1svLQIWhe2M8lv4wWRFXuby-1rCa3gCjfc9Yt5OSE8mcaahABun5_mhuDmyuNoDVlYAeAVJQzc9sHm7ZlGJephiHLBvEIk6abeuekqfvp_jGZiC2nbKO3_F1xDzEO9w4-Xo70IR1Oce7UyjmteIEHOsP9ii8OubmbQ7WNKlMC8FndFNI-VCbqiT1nzA_9Baej8UBi-3Q4pBHNPUvjQTTPw4-RKVpCdifTbeevnSgymJD7C_47V0DHTviBqlj5c2whChXC25z0iyG7NWAKO4b4xBh-3j6iMF8fO6wW6IUnITBv__ggNxuAMviomI-0QBE4J_jexVoiP80_5Ai-PNBRUou6HpJGVNeill7QHucvmi-BUtqcsdt_UVjydSA_yoHpfJE56e7snOJo8y-k9TmGxUXEtsZDky5fiJZsiGcoOtd09B6r4PXpXDy_MDKCJiT3fZy2gbyIHS9CNeAN2EPcledDlDsSdTbDo2VIFVrC-yoCczJHjvdlshe2YGFWIPpJ-CVf3wwZ0Pcw3EvfyKo5F1_M0re5nhLmGTRE3u-PNBWoVLi7_EUH8N5Ax1g-lPi5P3FutDv1nOYXWDhxEZop73N4Hpv71rmOrAA1_I4MqBSBvJGIrEZJ5fLMIXn8vW2pgY_aDJjnSR4iKDd2hqU9DBfhh6YZlTgGY5FVVY3HU1J6LtKbNQxg=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c09000063e5c3d1_0%7C0a220b774c0c0000c53091b6_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=E_g2qqSgt7-QIQeu7EkfIg3uxxS90OZwENsWd1Go-bgd9OttEVYeHfVePNP2h5YXN2x-wZowbpoZ_8w1L5hbYm8Snevts7qvx646eh4GGi-83eKUT_sqdWr1svLQIWhe2M8lv4wWRFXuby-1rCa3gCjfc9Yt5OSE8mcaahABun5_mhuDmyuNoDVlYAeAVJQzc9sHm7ZlGJephiHLBvEIk6abeuekqfvp_jGZiC2nbKO3_F1xDzEO9w4-Xo70IR1Oce7UyjmteIEHOsP9ii8OubmbQ7WNKlMC8FndFNI-VCbqiT1nzA_9Baej8UBi-3Q4pBHNPUvjQTTPw4-RKVpCdifTbeevnSgymJD7C_47V0DHTviBqlj5c2whChXC25z0iyG7NWAKO4b4xBh-3j6iMF8fO6wW6IUnITBv__ggNxuAMviomI-0QBE4J_jexVoiP80_5Ai-PNBRUou6HpJGVNeill7QHucvmi-BUtqcsdt_UVjydSA_yoHpfJE56e7snOJo8y-k9TmGxUXEtsZDky5fiJZsiGcoOtd09B6r4PXpXDy_MDKCJiT3fZy2gbyIHS9CNeAN2EPcledDlDsSdTbDo2VIFVrC-yoCczJHjvdlshe2YGFWIPpJ-CVf3wwZ0Pcw3EvfyKo5F1_M0re5nhLmGTRE3u-PNBWoVLi7_EUH8N5Ax1g-lPi5P3FutDv1nOYXWDhxEZop73N4Hpv71rmOrAA1_I4MqBSBvJGIrEZJ5fLMIXn8vW2pgY_aDJjnSR4iKDd2hqU9DBfhh6YZlTgGY5FVVY3HU1J6LtKbNQxg=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-04-18T10:15:00.000Z", "utc_arrival": "2023-04-18T08:15:00.000Z", "local_departure": "2023-04-18T06:55:00.000Z", "utc_departure": "2023-04-18T04:55:00.000Z"}, {"id": "0b770a224c390000dc0e5ade_0|0a220b774c3d0000a9239654_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 762.631517, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 233265.3654, "conversion": {"EUR": 610.631897, "HUF": 233265.3654}, "fare": {"adults": 116632.68, "children": 116632.68, "infants": 116632.68}, "bags_price": {"1": 75.068, "2": 159.95}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 158, "hold_height": 52, "hold_length": 78, "hold_weight": 20, "hold_width": 28, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 3, "personal_item_width": 15}, "availability": {"seats": 6}, "airlines": ["FR", "IB"], "route": [{"id": "0b770a224c390000dc0e5ade_0", "combination_id": "0b770a224c390000dc0e5ade", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-05T14:00:00.000Z", "utc_arrival": "2023-06-05T12:00:00.000Z", "local_departure": "2023-06-05T10:40:00.000Z", "utc_departure": "2023-06-05T08:40:00.000Z"}, {"id": "0a220b774c3d0000a9239654_0", "combination_id": "0a220b774c3d0000a9239654", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "IB", "flight_no": 3278, "operating_carrier": "IB", "operating_flight_no": "3278", "fare_basis": "VZNNAOB4", "fare_category": "M", "fare_classes": "V", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-09T14:55:00.000Z", "utc_arrival": "2023-06-09T12:55:00.000Z", "local_departure": "2023-06-09T11:45:00.000Z", "utc_departure": "2023-06-09T09:45:00.000Z"}], "booking_token": "E5IyeJEmgALkRPZUTaIzyTlnBcgIiONAympRrdFnbcEFG1bXLoUJ0aaw9RNVTah6kbe_Wszq4w7K2rg55Il6qfPDT9t5hddu7mvIsViH32Zsvh4Wh-NbDMClYH0FHVFAgMzf6IeLH7PS_iWk13I5ww4Ozwcqo0a0J3uxXTnRyEJQyLMrXL65oafuaZfzOLQb6JuL6_dDhp5_9fC9g6uZyGX1EgWl2JCyHjw4dXGb3RPWqTpY3EmdlzUt21FauoEZz2BM-eJKYnC90asmamid73GSBd9mQ_JJ0df4m36DCXuiMskAZwTJIZXz2Bh9gjyTRGoclSVL8tm65ojsNkOOk8aC_YChN-J57ZQGTu7MpoaZKVjB9hP64Iijs8Xn29zOB8X3EsihzdG3Zqs_qv5ouBXPzX55vhB3RLWoW9y7LbTajPzzv_hk6mx8jmvrBX-pNr37cstMT_yku1aaQ93G-X97Ed5w18VMoMLVbxmvOKBgJ1I-OmhdAx--4sLBwlE1l-vD-o1tXqkonO4LF46k9ZVR7Z4PC4T4FsoXn8MrGI_DXesgB1s9rxHxlepk1cX2f-hwh2oyluVclvUKFwn8DUrQmhyO_xk4ByLbbRp1yALD4r-EuAf7ZkuYImVHKn4nXStAgy1Mhm9UtFcot56YJnyxV_yxBckv941byPVTsQ65dKJIJIBKTWDkMnCxULMTyhGtbb0JpwIuQomS1JiH3jxvOOcRWKXCoUDxPA7TYFzo=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c390000dc0e5ade_0%7C0a220b774c3d0000a9239654_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=E5IyeJEmgALkRPZUTaIzyTlnBcgIiONAympRrdFnbcEFG1bXLoUJ0aaw9RNVTah6kbe_Wszq4w7K2rg55Il6qfPDT9t5hddu7mvIsViH32Zsvh4Wh-NbDMClYH0FHVFAgMzf6IeLH7PS_iWk13I5ww4Ozwcqo0a0J3uxXTnRyEJQyLMrXL65oafuaZfzOLQb6JuL6_dDhp5_9fC9g6uZyGX1EgWl2JCyHjw4dXGb3RPWqTpY3EmdlzUt21FauoEZz2BM-eJKYnC90asmamid73GSBd9mQ_JJ0df4m36DCXuiMskAZwTJIZXz2Bh9gjyTRGoclSVL8tm65ojsNkOOk8aC_YChN-J57ZQGTu7MpoaZKVjB9hP64Iijs8Xn29zOB8X3EsihzdG3Zqs_qv5ouBXPzX55vhB3RLWoW9y7LbTajPzzv_hk6mx8jmvrBX-pNr37cstMT_yku1aaQ93G-X97Ed5w18VMoMLVbxmvOKBgJ1I-OmhdAx--4sLBwlE1l-vD-o1tXqkonO4LF46k9ZVR7Z4PC4T4FsoXn8MrGI_DXesgB1s9rxHxlepk1cX2f-hwh2oyluVclvUKFwn8DUrQmhyO_xk4ByLbbRp1yALD4r-EuAf7ZkuYImVHKn4nXStAgy1Mhm9UtFcot56YJnyxV_yxBckv941byPVTsQ65dKJIJIBKTWDkMnCxULMTyhGtbb0JpwIuQomS1JiH3jxvOOcRWKXCoUDxPA7TYFzo=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-05T14:00:00.000Z", "utc_arrival": "2023-06-05T12:00:00.000Z", "local_departure": "2023-06-05T10:40:00.000Z", "utc_departure": "2023-06-05T08:40:00.000Z"}, {"id": "0b770a224c470000f72dd482_0|0a220b774c4b0000292d2891_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 765.467904, "distance": 1975.87, "duration": {"departure": 12600, "return": 11400, "total": 24000}, "price": 233330.2022, "conversion": {"EUR": 610.801624, "HUF": 233330.2022}, "fare": {"adults": 116665.1, "children": 116665.1, "infants": 116665.1}, "bags_price": {"1": 100.1, "2": 200.214}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 5}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224c470000f72dd482_0", "combination_id": "0b770a224c470000f72dd482", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-19T19:45:00.000Z", "utc_arrival": "2023-06-19T17:45:00.000Z", "local_departure": "2023-06-19T16:15:00.000Z", "utc_departure": "2023-06-19T14:15:00.000Z"}, {"id": "0a220b774c4b0000292d2891_0", "combination_id": "0a220b774c4b0000292d2891", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-23T18:00:00.000Z", "utc_arrival": "2023-06-23T16:00:00.000Z", "local_departure": "2023-06-23T14:50:00.000Z", "utc_departure": "2023-06-23T12:50:00.000Z"}], "booking_token": "E5pwOYsnDHt5Patg2malhMrlaYr8Lk2kftkUuieNpoCWtPmp3j_qCYEUO1Jk8kHJ1qmn-_VumUCuMT0qLzjpjd1UFuvOIwCM44SGi7TLRFmekSH3zeo-eprTyZ7nfRY6COQx5HuJgGn9MV0XnK8Dg7O0y7FA1eU-VVHCLijHv7WsHjdxSWQQjVFR5FNmnfzADUtRCRWKdanxyAi0lzGYqA-RQn0iAQJ3FnlD6ze4UUnnrXHeWBpAZV5yN3BBqwAfl2eWCMumrTLnJyVxhYB7tpoWDvS9P4tdSDU0eOHXCrXQ8Jvh5A8aJ-x3qP2rOR0t6BpPUqDCXmFdhduldC0FrkPsJ5pHSLZpk7MCHgaMuRh5UlkcYJ5Rmq8ThI70labpzprNfgpmLcQJPrT_Bshz2x2VEKeFn6bZzWoZ_yIIQxp0kqEtDflKo7DOOXtrljiYQrgtSPl4kqLfY7jKSh8W-ytcy9ASa1mo7DqMgMRYph7MAVnHMStSdMasoPvMA5pG4vH1kxpeeUdP8QQGc_z1DJfbgnJ6Q-9iNhcCy-9gf-y4Lo_F-xtDElq6QvnCDrDtFr4au2pQd_cxxgrQXnVoD3Zr5hC-lAJKHhPDh1gUVgDdHYG6TCSYvGYAMWG8Xri9ab4bdrkckwRKsIKxpV4rzOj_oaOVHHvQpdWVXhxgzL0knZhEWuB05iNA_pISVYfKwA863I4Uo-l0NUIouiUv3bDQ_kSohAdbl_lPmzlBzrhPcMu6_oNG6qwjGut8Rm-lbCZCN7I_hoMoPXPQEALlsUw==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c470000f72dd482_0%7C0a220b774c4b0000292d2891_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=E5pwOYsnDHt5Patg2malhMrlaYr8Lk2kftkUuieNpoCWtPmp3j_qCYEUO1Jk8kHJ1qmn-_VumUCuMT0qLzjpjd1UFuvOIwCM44SGi7TLRFmekSH3zeo-eprTyZ7nfRY6COQx5HuJgGn9MV0XnK8Dg7O0y7FA1eU-VVHCLijHv7WsHjdxSWQQjVFR5FNmnfzADUtRCRWKdanxyAi0lzGYqA-RQn0iAQJ3FnlD6ze4UUnnrXHeWBpAZV5yN3BBqwAfl2eWCMumrTLnJyVxhYB7tpoWDvS9P4tdSDU0eOHXCrXQ8Jvh5A8aJ-x3qP2rOR0t6BpPUqDCXmFdhduldC0FrkPsJ5pHSLZpk7MCHgaMuRh5UlkcYJ5Rmq8ThI70labpzprNfgpmLcQJPrT_Bshz2x2VEKeFn6bZzWoZ_yIIQxp0kqEtDflKo7DOOXtrljiYQrgtSPl4kqLfY7jKSh8W-ytcy9ASa1mo7DqMgMRYph7MAVnHMStSdMasoPvMA5pG4vH1kxpeeUdP8QQGc_z1DJfbgnJ6Q-9iNhcCy-9gf-y4Lo_F-xtDElq6QvnCDrDtFr4au2pQd_cxxgrQXnVoD3Zr5hC-lAJKHhPDh1gUVgDdHYG6TCSYvGYAMWG8Xri9ab4bdrkckwRKsIKxpV4rzOj_oaOVHHvQpdWVXhxgzL0knZhEWuB05iNA_pISVYfKwA863I4Uo-l0NUIouiUv3bDQ_kSohAdbl_lPmzlBzrhPcMu6_oNG6qwjGut8Rm-lbCZCN7I_hoMoPXPQEALlsUw==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-19T19:45:00.000Z", "utc_arrival": "2023-06-19T17:45:00.000Z", "local_departure": "2023-06-19T16:15:00.000Z", "utc_departure": "2023-06-19T14:15:00.000Z"}, {"id": "0b770a224c1900003bb4006b_0|0a220b774c1d000091abd9a6_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 767.703402, "distance": 1975.87, "duration": {"departure": 12600, "return": 11700, "total": 24300}, "price": 233674.8362, "conversion": {"EUR": 611.703792, "HUF": 233674.8362}, "fare": {"adults": 116837.42, "children": 120065.33, "infants": 120065.33}, "bags_price": {"1": 98.56, "2": 197.134}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 439, "hold_height": 149, "hold_length": 171, "hold_weight": 20, "hold_width": 119, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 3}, "airlines": ["W6"], "route": [{"id": "0b770a224c1900003bb4006b_0", "combination_id": "0b770a224c1900003bb4006b", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "KLREG", "fare_category": "M", "fare_classes": "K", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-04T21:15:00.000Z", "utc_arrival": "2023-05-04T19:15:00.000Z", "local_departure": "2023-05-04T17:45:00.000Z", "utc_departure": "2023-05-04T15:45:00.000Z"}, {"id": "0a220b774c1d000091abd9a6_0", "combination_id": "0a220b774c1d000091abd9a6", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "GREG", "fare_category": "M", "fare_classes": "G", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-08T23:45:00.000Z", "utc_arrival": "2023-05-08T21:45:00.000Z", "local_departure": "2023-05-08T20:30:00.000Z", "utc_departure": "2023-05-08T18:30:00.000Z"}], "booking_token": "EZsX8Ga_tP0DNCUIagA2jLgyV9zL83vEwMPMoJnNR7IF5hzsA-KvBu9p_rprgRm1xFve8jL1eZJYnK5DbZ_tqBqOW4UlVFAXfL2hvlgBaYcbZPrawlggfl27QWF5bZri1rduvB8TMhfAkkCUJOqfrBbfzJwsBFEG_b2BTYv5sO9A6_5zLHRLh_auWMNcv_vNr7PDmWmY2MpDFeqbZBfgIrjARSpCEWP7nYBo1a5LvseHNlkpMIpn2hcqldrmMFp9eutbt-HfnCVF8LcKLLIh-H5Y275vYCtknWumGGqG3_vXmRiTlR2UlGrRLWLU4AlChEmLb2gKlEWlwjOS_W-ZOzVRFYpvfaKnonV_2HgEtRDDcKviTXEJAU3sJ_RBUv-M3TrvwV1uam9qpr6PcUN7SMcABqpsoHxTUAUvZ-NvqccZIvC0mRJxoPdgGXI6xb0-MNvU0k8nFlvCVn61NZ4j38O28TSf1gXUMXBbnHdIw7uTc8sX7OoMj36C-KAd15iV25-e1R1opoDV_2Yzqbf6A1vj1ba0_tz9kUhTj6JcmBUfpaS8jgE-WnLH76wgdYJdyaB4ivnO9JrPd3d4BUj8gsyJr2ZmkQJig5S5FjOVoW_dO2y2XW_gIASIRgriDd3GiPaQTUT7qT6N6NivuMBdgkLfZ_INHkDPlg6l9UQHJlVlPBihUHCm63cD1A4XLQPfNqL_ULOLDjw_dnypdRVivXLsdAHNwThLReMd4R7ID0l7czP6lsnFgmLuwNsm7qHmW__RN8IUlUeX6qv1YFoTJZZO6fPF3mTffAs82SXXfeNrRCe9HzXEaS34IS_PCkkIe", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c1900003bb4006b_0%7C0a220b774c1d000091abd9a6_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EZsX8Ga_tP0DNCUIagA2jLgyV9zL83vEwMPMoJnNR7IF5hzsA-KvBu9p_rprgRm1xFve8jL1eZJYnK5DbZ_tqBqOW4UlVFAXfL2hvlgBaYcbZPrawlggfl27QWF5bZri1rduvB8TMhfAkkCUJOqfrBbfzJwsBFEG_b2BTYv5sO9A6_5zLHRLh_auWMNcv_vNr7PDmWmY2MpDFeqbZBfgIrjARSpCEWP7nYBo1a5LvseHNlkpMIpn2hcqldrmMFp9eutbt-HfnCVF8LcKLLIh-H5Y275vYCtknWumGGqG3_vXmRiTlR2UlGrRLWLU4AlChEmLb2gKlEWlwjOS_W-ZOzVRFYpvfaKnonV_2HgEtRDDcKviTXEJAU3sJ_RBUv-M3TrvwV1uam9qpr6PcUN7SMcABqpsoHxTUAUvZ-NvqccZIvC0mRJxoPdgGXI6xb0-MNvU0k8nFlvCVn61NZ4j38O28TSf1gXUMXBbnHdIw7uTc8sX7OoMj36C-KAd15iV25-e1R1opoDV_2Yzqbf6A1vj1ba0_tz9kUhTj6JcmBUfpaS8jgE-WnLH76wgdYJdyaB4ivnO9JrPd3d4BUj8gsyJr2ZmkQJig5S5FjOVoW_dO2y2XW_gIASIRgriDd3GiPaQTUT7qT6N6NivuMBdgkLfZ_INHkDPlg6l9UQHJlVlPBihUHCm63cD1A4XLQPfNqL_ULOLDjw_dnypdRVivXLsdAHNwThLReMd4R7ID0l7czP6lsnFgmLuwNsm7qHmW__RN8IUlUeX6qv1YFoTJZZO6fPF3mTffAs82SXXfeNrRCe9HzXEaS34IS_PCkkIe", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-04T21:15:00.000Z", "utc_arrival": "2023-05-04T19:15:00.000Z", "local_departure": "2023-05-04T17:45:00.000Z", "utc_departure": "2023-05-04T15:45:00.000Z"}, {"id": "0b770a224c440000bf45cd3f_0|0a220b774c4700009310bb78_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 763.154449, "distance": 1975.87, "duration": {"departure": 11700, "return": 11400, "total": 23100}, "price": 233974.4695, "conversion": {"EUR": 612.488159, "HUF": 233974.4695}, "fare": {"adults": 116987.23, "children": 116987.23, "infants": 116987.23}, "bags_price": {"1": 82.586, "2": 174.972}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 158, "hold_height": 52, "hold_length": 78, "hold_weight": 20, "hold_width": 28, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 3, "personal_item_width": 15}, "availability": {"seats": 2}, "airlines": ["FR", "IB"], "route": [{"id": "0b770a224c440000bf45cd3f_0", "combination_id": "0b770a224c440000bf45cd3f", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "IB", "flight_no": 3279, "operating_carrier": "IB", "operating_flight_no": "3279", "fare_basis": "VZNNAOB4", "fare_category": "M", "fare_classes": "V", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-16T18:50:00.000Z", "utc_arrival": "2023-06-16T16:50:00.000Z", "local_departure": "2023-06-16T15:35:00.000Z", "utc_departure": "2023-06-16T13:35:00.000Z"}, {"id": "0a220b774c4700009310bb78_0", "combination_id": "0a220b774c4700009310bb78", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-19T10:15:00.000Z", "utc_arrival": "2023-06-19T08:15:00.000Z", "local_departure": "2023-06-19T07:05:00.000Z", "utc_departure": "2023-06-19T05:05:00.000Z"}], "booking_token": "EqobwSJw8bAnZ7kTaQxjMtaMIu_UrT74kDu2iW4WkXnA1V9m41HPv0qQP5HreCV9ZmZPfLSH3J93jkQg-DXtJ9MYma66CrE-AATIcbDIR4AE2o_9AE1v19TcHPVdcxxy9XQfiFOGzmYFKru_9gFcsyuW1sz231eUMXRHFhNUQC59c-t_HvoftN4Nl8OENzlw1c6e64WakBoYYPlo-g5jgNMmBbuw2TIwaddwomBf_0Sxo7ULDuaL67d2CzWa-I2oEuRtKba357f6Im-6isOVRipAsvoh17eSbxIkGSL8-m7g6fQGmLQ1yOJQFxNvjMhvQiav82xY-tajXEPH1C9o7442Zt3Mvdxy3JMXWhfR0fIqeEacB9rOXoK5oKLchVkpsNDprjqL01Uw4vp30Mn5gOBDn9MWIK6xjpfwG88v2ZJObOP8CO7GmN10st3TbCh_YOEtLJ7F8No5d8HmEdiGxZZ820HC5ayCyXAZjsNf_7I2ly_EOwGEMRY2euJgG2NI89rcCE19aKwu17aCAr7GH95GUTgk76CT8sbfTVqQLwsVgAf1sp2LW4TK3gyEPG7MpbBS2jQUeJKf2BkSh93Kc-H5Z6cfFlqrGJNNGNkblyDOZxWk8M29nn4a-Q-AG9RB-lj0puTxEC019Oozipz9Sqh0umQJVZMixpEHzrA6u7q9Fed1wOZ6nyw--bXexYRQkB9mDPn4jSEZ3PK_PqR5HWMesUiY8yhlob6mPRYCe0evM-y9VSjWq32RDH-CwLjeikUylZk1nUyE_MRzuuMUsxK54Z8viSW9Ap5WBAJpwLlI=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c440000bf45cd3f_0%7C0a220b774c4700009310bb78_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EqobwSJw8bAnZ7kTaQxjMtaMIu_UrT74kDu2iW4WkXnA1V9m41HPv0qQP5HreCV9ZmZPfLSH3J93jkQg-DXtJ9MYma66CrE-AATIcbDIR4AE2o_9AE1v19TcHPVdcxxy9XQfiFOGzmYFKru_9gFcsyuW1sz231eUMXRHFhNUQC59c-t_HvoftN4Nl8OENzlw1c6e64WakBoYYPlo-g5jgNMmBbuw2TIwaddwomBf_0Sxo7ULDuaL67d2CzWa-I2oEuRtKba357f6Im-6isOVRipAsvoh17eSbxIkGSL8-m7g6fQGmLQ1yOJQFxNvjMhvQiav82xY-tajXEPH1C9o7442Zt3Mvdxy3JMXWhfR0fIqeEacB9rOXoK5oKLchVkpsNDprjqL01Uw4vp30Mn5gOBDn9MWIK6xjpfwG88v2ZJObOP8CO7GmN10st3TbCh_YOEtLJ7F8No5d8HmEdiGxZZ820HC5ayCyXAZjsNf_7I2ly_EOwGEMRY2euJgG2NI89rcCE19aKwu17aCAr7GH95GUTgk76CT8sbfTVqQLwsVgAf1sp2LW4TK3gyEPG7MpbBS2jQUeJKf2BkSh93Kc-H5Z6cfFlqrGJNNGNkblyDOZxWk8M29nn4a-Q-AG9RB-lj0puTxEC019Oozipz9Sqh0umQJVZMixpEHzrA6u7q9Fed1wOZ6nyw--bXexYRQkB9mDPn4jSEZ3PK_PqR5HWMesUiY8yhlob6mPRYCe0evM-y9VSjWq32RDH-CwLjeikUylZk1nUyE_MRzuuMUsxK54Z8viSW9Ap5WBAJpwLlI=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-16T18:50:00.000Z", "utc_arrival": "2023-06-16T16:50:00.000Z", "local_departure": "2023-06-16T15:35:00.000Z", "utc_departure": "2023-06-16T13:35:00.000Z"}, {"id": "0b770a224c440000087d9250_0|0a220b774c47000069bc4867_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 766.223037, "distance": 1975.87, "duration": {"departure": 12000, "return": 11700, "total": 23700}, "price": 234128.0087, "conversion": {"EUR": 612.890087, "HUF": 234128.0087}, "fare": {"adults": 117064, "children": 117064, "infants": 117064}, "bags_price": {"1": 99.4, "2": 198.786}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 3}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224c440000087d9250_0", "combination_id": "0b770a224c440000087d9250", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-16T21:45:00.000Z", "utc_arrival": "2023-06-16T19:45:00.000Z", "local_departure": "2023-06-16T18:25:00.000Z", "utc_departure": "2023-06-16T16:25:00.000Z"}, {"id": "0a220b774c47000069bc4867_0", "combination_id": "0a220b774c47000069bc4867", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-19T23:45:00.000Z", "utc_arrival": "2023-06-19T21:45:00.000Z", "local_departure": "2023-06-19T20:30:00.000Z", "utc_departure": "2023-06-19T18:30:00.000Z"}], "booking_token": "Eesq48Zv7Fhvy_fbYmNxKEMqFDhPoxSqGWN9X_Nd6CVygAnseTIJ6TTDRm7I-NvFpO4Fysd1A8QZEGc4SAYkhxLTJXruYEhNY-vBZZCIR2ByMbpZ0aGQVqOdmhQjeRWEw8-HAnfmDJizW9pcti6mbKQ5_UlvKC5QpDnY8AD1eYEBEAUAcKfWzs9E5ubPq-3wLHNWlu6k9Y-WTPT_LNyIWNH0HgjP5o8Fydblueh90KJJcWZwePr3ELZt-7zrGF18IvGR_rbCs3aDfeo34OscZqbpxIYrSX9yVZUAPcAf16YreK1v-_ETN7Q0oHRr2D_hcF4wUzgASLLyRNQYR2BkhYz5FAMW5nG-V-dk3Twud2V1PIVg90q5QxAl69rAmV0yIY_m1lbjLOS_oilcEw0vVfM2qouXaJMhxK5A4UjlqL-D5BvN-AdZ2hxCGnNDG6chDBAc_0l5EmPjIWu5Mo3k7ycos-5w1sB45G_P-zP2Jh1R2M8GvsPGDdmUSvmCWGdXWIRcjWoQlA2f6p1H73FVvw08ppQkAmZTjRiec3ZO3smuYvdATqPrBqwjmCYs5F3CXJ_O2wQ59YMyHE08t7tjHIxO7jDUkaIiKBPuyM24IwoByzPAfb0oDJaG2uKMTGKzA3SDGr_jdaUPQjzXCYW5X73UHVTA8sfAe6dGgm1YW5N7s7zEqXkSyBXQfl_MjiEY_l1zTX8t9XQk4n_ul19Ko5-vWnC3l5nwlqaXXxEI1Or7tAKLMVcKI1KM4kjnuQnFvRUYBVL8SNpdY8zdQVQXo79nLj8kpRnbNfsw072iFuHo=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c440000087d9250_0%7C0a220b774c47000069bc4867_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=Eesq48Zv7Fhvy_fbYmNxKEMqFDhPoxSqGWN9X_Nd6CVygAnseTIJ6TTDRm7I-NvFpO4Fysd1A8QZEGc4SAYkhxLTJXruYEhNY-vBZZCIR2ByMbpZ0aGQVqOdmhQjeRWEw8-HAnfmDJizW9pcti6mbKQ5_UlvKC5QpDnY8AD1eYEBEAUAcKfWzs9E5ubPq-3wLHNWlu6k9Y-WTPT_LNyIWNH0HgjP5o8Fydblueh90KJJcWZwePr3ELZt-7zrGF18IvGR_rbCs3aDfeo34OscZqbpxIYrSX9yVZUAPcAf16YreK1v-_ETN7Q0oHRr2D_hcF4wUzgASLLyRNQYR2BkhYz5FAMW5nG-V-dk3Twud2V1PIVg90q5QxAl69rAmV0yIY_m1lbjLOS_oilcEw0vVfM2qouXaJMhxK5A4UjlqL-D5BvN-AdZ2hxCGnNDG6chDBAc_0l5EmPjIWu5Mo3k7ycos-5w1sB45G_P-zP2Jh1R2M8GvsPGDdmUSvmCWGdXWIRcjWoQlA2f6p1H73FVvw08ppQkAmZTjRiec3ZO3smuYvdATqPrBqwjmCYs5F3CXJ_O2wQ59YMyHE08t7tjHIxO7jDUkaIiKBPuyM24IwoByzPAfb0oDJaG2uKMTGKzA3SDGr_jdaUPQjzXCYW5X73UHVTA8sfAe6dGgm1YW5N7s7zEqXkSyBXQfl_MjiEY_l1zTX8t9XQk4n_ul19Ko5-vWnC3l5nwlqaXXxEI1Or7tAKLMVcKI1KM4kjnuQnFvRUYBVL8SNpdY8zdQVQXo79nLj8kpRnbNfsw072iFuHo=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-16T21:45:00.000Z", "utc_arrival": "2023-06-16T19:45:00.000Z", "local_departure": "2023-06-16T18:25:00.000Z", "utc_departure": "2023-06-16T16:25:00.000Z"}, {"id": "0b770a224c420000e2660c77_0|0a220b774c46000040adc89d_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 767.02466, "distance": 1975.87, "duration": {"departure": 11700, "return": 11700, "total": 23400}, "price": 234943.5746, "conversion": {"EUR": 615.02504, "HUF": 234943.5746}, "fare": {"adults": 117471.79, "children": 117471.79, "infants": 117471.79}, "bags_price": {"1": 97.118, "2": 204.036}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 158, "hold_height": 52, "hold_length": 78, "hold_weight": 20, "hold_width": 28, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 3, "personal_item_width": 15}, "availability": {"seats": 6}, "airlines": ["W6", "IB"], "route": [{"id": "0b770a224c420000e2660c77_0", "combination_id": "0b770a224c420000e2660c77", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "IB", "flight_no": 3279, "operating_carrier": "IB", "operating_flight_no": "3279", "fare_basis": "NZNNAOB4", "fare_category": "M", "fare_classes": "N", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-14T18:50:00.000Z", "utc_arrival": "2023-06-14T16:50:00.000Z", "local_departure": "2023-06-14T15:35:00.000Z", "utc_departure": "2023-06-14T13:35:00.000Z"}, {"id": "0a220b774c46000040adc89d_0", "combination_id": "0a220b774c46000040adc89d", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "JREG", "fare_category": "M", "fare_classes": "J", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-18T21:05:00.000Z", "utc_arrival": "2023-06-18T19:05:00.000Z", "local_departure": "2023-06-18T17:50:00.000Z", "utc_departure": "2023-06-18T15:50:00.000Z"}], "booking_token": "E3gkCoa1zKuiOAqtgh5IoGx2Usl-KlWm25CZ-95VLLQuw-6_0VyutIMjRx3KJq2Rjc2ujT9z3_FqiuGsh1o7tNVLYIv3eR8grD-KO6oAqfCpyG8Fa-tPdLBGroW0rAbkLZwSUzcS_pDMkrdrewTji6w92EhKFG2ioyuYzaJSsTc_BKyzVgOsry3zaDm5qNAHqSNMH4LXpojl_gllbxaNdxeY4Iwi9de8LoblRbb5FAHPXCit2rFL9A1N4PaBA0duto9oi1QsNh9mUcPt4_VxZu0fQWW2mqTjzCeaEkx-vMG_TY5emEcIy-bmsvhAzrDSyU00LbbsxMzBu19s9BTh1752JY4bM-B4LHfJMPqDMdHciINFDyoJiOLNFFl-yiR9UrcNOxomW0U5MIDF_338gm_PYtIq8HlDYdw6QDCQIsz4vF2lLcISJGXiRwi48f9fgaSMDGH0hUvkPjyyAs5sVZNBCffvd4PVnqPJPkJbMb61HTOwbv6gNHJjQARcDjq_Knf5puIiMXNlxqQrmgVDPlKzHlVkZsOYeO9IO8jXUEEywFQXxjIdgOcoH3cBi3NrAo4cu5iubfJ7bEXFN6GmZJWPL5x2CUvFs2SE_qM_K_2RNk5uiV4NfVGwcNzY92aiDLkYMTILD6ExA4nQOt5RNXKOZIbJbeLzZboVSmiD-FiJGaA0Sl2lOMFLnqKoCftcQjstEDw7eOg1vyzzJo8fq1ynrjSJMfAeklUAxDKwvQWTswofqGzXh3DinqZQfLO1as5oMwn93zySFAMEe6GyzHj_ywQhPbC6lKvEIcbhlEKQ=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c420000e2660c77_0%7C0a220b774c46000040adc89d_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=E3gkCoa1zKuiOAqtgh5IoGx2Usl-KlWm25CZ-95VLLQuw-6_0VyutIMjRx3KJq2Rjc2ujT9z3_FqiuGsh1o7tNVLYIv3eR8grD-KO6oAqfCpyG8Fa-tPdLBGroW0rAbkLZwSUzcS_pDMkrdrewTji6w92EhKFG2ioyuYzaJSsTc_BKyzVgOsry3zaDm5qNAHqSNMH4LXpojl_gllbxaNdxeY4Iwi9de8LoblRbb5FAHPXCit2rFL9A1N4PaBA0duto9oi1QsNh9mUcPt4_VxZu0fQWW2mqTjzCeaEkx-vMG_TY5emEcIy-bmsvhAzrDSyU00LbbsxMzBu19s9BTh1752JY4bM-B4LHfJMPqDMdHciINFDyoJiOLNFFl-yiR9UrcNOxomW0U5MIDF_338gm_PYtIq8HlDYdw6QDCQIsz4vF2lLcISJGXiRwi48f9fgaSMDGH0hUvkPjyyAs5sVZNBCffvd4PVnqPJPkJbMb61HTOwbv6gNHJjQARcDjq_Knf5puIiMXNlxqQrmgVDPlKzHlVkZsOYeO9IO8jXUEEywFQXxjIdgOcoH3cBi3NrAo4cu5iubfJ7bEXFN6GmZJWPL5x2CUvFs2SE_qM_K_2RNk5uiV4NfVGwcNzY92aiDLkYMTILD6ExA4nQOt5RNXKOZIbJbeLzZboVSmiD-FiJGaA0Sl2lOMFLnqKoCftcQjstEDw7eOg1vyzzJo8fq1ynrjSJMfAeklUAxDKwvQWTswofqGzXh3DinqZQfLO1as5oMwn93zySFAMEe6GyzHj_ywQhPbC6lKvEIcbhlEKQ=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-14T18:50:00.000Z", "utc_arrival": "2023-06-14T16:50:00.000Z", "local_departure": "2023-06-14T15:35:00.000Z", "utc_departure": "2023-06-14T13:35:00.000Z"}, {"id": "0b770a224c360000d7613bb9_0|0a220b774c390000ac91a717_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 766.074417, "distance": 1975.87, "duration": {"departure": 11700, "return": 11400, "total": 23100}, "price": 235089.9164, "conversion": {"EUR": 615.408127, "HUF": 235089.9164}, "fare": {"adults": 117544.96, "children": 117544.96, "infants": 117544.96}, "bags_price": {"1": 73.486, "2": 156.772}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 158, "hold_height": 52, "hold_length": 78, "hold_weight": 20, "hold_width": 28, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 3, "personal_item_width": 15}, "availability": {"seats": 2}, "airlines": ["FR", "IB"], "route": [{"id": "0b770a224c360000d7613bb9_0", "combination_id": "0b770a224c360000d7613bb9", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "IB", "flight_no": 3279, "operating_carrier": "IB", "operating_flight_no": "3279", "fare_basis": "SZNNAOB4", "fare_category": "M", "fare_classes": "S", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-02T18:50:00.000Z", "utc_arrival": "2023-06-02T16:50:00.000Z", "local_departure": "2023-06-02T15:35:00.000Z", "utc_departure": "2023-06-02T13:35:00.000Z"}, {"id": "0a220b774c390000ac91a717_0", "combination_id": "0a220b774c390000ac91a717", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-05T10:15:00.000Z", "utc_arrival": "2023-06-05T08:15:00.000Z", "local_departure": "2023-06-05T07:05:00.000Z", "utc_departure": "2023-06-05T05:05:00.000Z"}], "booking_token": "EVrf9C8b_mFEO5yxbEPHRuCUse_9Ab2AWu02j-c-Y8LF58h0TlK816_42assdaQpjF94nNofGFv6fgS9QpiWpZ39EJVBhAOl9NC8sOik7IHgTGVtywU99hexWBdkZVAnMzodHh7PVQs8m3f8EpZVSJTsz-CZz_k5TF8fEULCczywZopQ-vB8FyjPRqFxRU5U3bL3StPxGIZUngAEzzyBHNCFuKNgHxbn3Tqjqc82n39QN2_HoF1J1PlVitMZMFTR-ABhLovUK8tehZm8BTIVOVUmtQIMbyshHvmngjlELMlCKOzFk_dwIWySq8-wa-gzxVeuJrjc6sIfeI-biEygCY2DhtXPI7pVC5Pbdm_PkzQf5LKlINfcRhTOBYykU9F_GOP3iz8D-2WnCP0kUMgKl14tH1EQyDAT7nK_ISOZEE9BkJRu2aUTs4A_TE133xiJR8QI0NtEapFOOu7RrZXY4yWcvuFBQ2o-Cqcdc1_R1jQ0GD6EmsgjjhxZcr4kMaf-QK_gXn-tBGak1ZLfSaN_84OpPpAvUZG8YrhT2hjqa1bhg3EkJnRko8_xs27tVZ5_xBNI5TRCMv2r5lbHLNuZBv-nCUgzhQhvTvEasiO7TJZbKpIH5U4A9aJcoJ9XcO3HisWSMRJ8pMa926qSg-ztUhMLwV4TZ8w1DOfKj50UlMK9qZaMFIUVC3iux7LUUn_K-OSYe1GsgzLcQdrFqTmrnoUzatIoh5VvtszCGlP9D9mOcWZa1A5uNoWsB7lkguCjSYNYHpTD8DWsbpR87YZcsgl4luAq0xXyMe7lrOQZWmNw=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c360000d7613bb9_0%7C0a220b774c390000ac91a717_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EVrf9C8b_mFEO5yxbEPHRuCUse_9Ab2AWu02j-c-Y8LF58h0TlK816_42assdaQpjF94nNofGFv6fgS9QpiWpZ39EJVBhAOl9NC8sOik7IHgTGVtywU99hexWBdkZVAnMzodHh7PVQs8m3f8EpZVSJTsz-CZz_k5TF8fEULCczywZopQ-vB8FyjPRqFxRU5U3bL3StPxGIZUngAEzzyBHNCFuKNgHxbn3Tqjqc82n39QN2_HoF1J1PlVitMZMFTR-ABhLovUK8tehZm8BTIVOVUmtQIMbyshHvmngjlELMlCKOzFk_dwIWySq8-wa-gzxVeuJrjc6sIfeI-biEygCY2DhtXPI7pVC5Pbdm_PkzQf5LKlINfcRhTOBYykU9F_GOP3iz8D-2WnCP0kUMgKl14tH1EQyDAT7nK_ISOZEE9BkJRu2aUTs4A_TE133xiJR8QI0NtEapFOOu7RrZXY4yWcvuFBQ2o-Cqcdc1_R1jQ0GD6EmsgjjhxZcr4kMaf-QK_gXn-tBGak1ZLfSaN_84OpPpAvUZG8YrhT2hjqa1bhg3EkJnRko8_xs27tVZ5_xBNI5TRCMv2r5lbHLNuZBv-nCUgzhQhvTvEasiO7TJZbKpIH5U4A9aJcoJ9XcO3HisWSMRJ8pMa926qSg-ztUhMLwV4TZ8w1DOfKj50UlMK9qZaMFIUVC3iux7LUUn_K-OSYe1GsgzLcQdrFqTmrnoUzatIoh5VvtszCGlP9D9mOcWZa1A5uNoWsB7lkguCjSYNYHpTD8DWsbpR87YZcsgl4luAq0xXyMe7lrOQZWmNw=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-02T18:50:00.000Z", "utc_arrival": "2023-06-02T16:50:00.000Z", "local_departure": "2023-06-02T15:35:00.000Z", "utc_departure": "2023-06-02T13:35:00.000Z"}, {"id": "0b770a224c3500005ea303c4_0|0a220b774c390000ac91a717_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 766.074417, "distance": 1975.87, "duration": {"departure": 11700, "return": 11400, "total": 23100}, "price": 235089.9164, "conversion": {"EUR": 615.408127, "HUF": 235089.9164}, "fare": {"adults": 117544.96, "children": 117544.96, "infants": 117544.96}, "bags_price": {"1": 73.486, "2": 156.772}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 158, "hold_height": 52, "hold_length": 78, "hold_weight": 20, "hold_width": 28, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 3, "personal_item_width": 15}, "availability": {"seats": 2}, "airlines": ["FR", "IB"], "route": [{"id": "0b770a224c3500005ea303c4_0", "combination_id": "0b770a224c3500005ea303c4", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "IB", "flight_no": 3279, "operating_carrier": "IB", "operating_flight_no": "3279", "fare_basis": "SZNNAOB4", "fare_category": "M", "fare_classes": "S", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-01T18:50:00.000Z", "utc_arrival": "2023-06-01T16:50:00.000Z", "local_departure": "2023-06-01T15:35:00.000Z", "utc_departure": "2023-06-01T13:35:00.000Z"}, {"id": "0a220b774c390000ac91a717_0", "combination_id": "0a220b774c390000ac91a717", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-05T10:15:00.000Z", "utc_arrival": "2023-06-05T08:15:00.000Z", "local_departure": "2023-06-05T07:05:00.000Z", "utc_departure": "2023-06-05T05:05:00.000Z"}], "booking_token": "EiYFK5rglWMk9IhCuRKhA0nC-KNqgoXk8H_8KSFXZGa6JWu_b26H4BwKqFn4BaJ-LLjdfiGQymS6AWpq-tguKnmgmC4ISEe50dNNh-DIW7keI05y0yr5dnBp_lr7CP52WfDZM2hSJIpFc6Mc8W3SmIbm6YMxvyzWvY1JrxKsWbHMFaoOaQF2wSj9TqcAuTEBOuDLg-NcqWR18icKIUZGPCA9UOWknIMYMcX4l6DdsicCIQ_fX5iYGSpdZYN_km6pDR9Tv8Kkj3I5Mi89Z8EEauaILFwJfDq7xLxG3tsTDkcJb91OGG_mD0NK8XrJw7eqk7SdVNsHQkIT3SSYSX3DbI8qLytGZHn0yQheAN3Hg0nmuY23_OQTpOweUsqNJxPOkaBLT6eE2GAG80FDDgImv4W4shGdRkdfYMXgL5n4uhKXJ0DIDFdA5eSo4CxM-hdssSe4rtNHHtH9F0aMFJHXYjM1uPumqa58aziLvS3cwZHEEPq3_8RQv0NFzB_j62kuHBThpYx_gLJudWNgyaOCpVXXxDxc9V1BPrnYcOhp56MHxcjV41Q5SSVWNXkZjwjzZRf9CyF0JdO1FRzOHJKv_ein8qPh2zWsqrqE_d16thyfHlHNuteCw7dcthVQR_2w5LkjdXedkRI3LyO_7O0gE5hHCErMOnlNMQDssWndTicx0-2V14Qtto_AVjOTyJcN-fBbNzxWcYifC798-FHcYrV1EnXdpAiyJYk27X-E93V31juuzN7WLM3SOvEfdEr_4z_-jhDYAtlrAcJi2Q-2k2A==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c3500005ea303c4_0%7C0a220b774c390000ac91a717_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EiYFK5rglWMk9IhCuRKhA0nC-KNqgoXk8H_8KSFXZGa6JWu_b26H4BwKqFn4BaJ-LLjdfiGQymS6AWpq-tguKnmgmC4ISEe50dNNh-DIW7keI05y0yr5dnBp_lr7CP52WfDZM2hSJIpFc6Mc8W3SmIbm6YMxvyzWvY1JrxKsWbHMFaoOaQF2wSj9TqcAuTEBOuDLg-NcqWR18icKIUZGPCA9UOWknIMYMcX4l6DdsicCIQ_fX5iYGSpdZYN_km6pDR9Tv8Kkj3I5Mi89Z8EEauaILFwJfDq7xLxG3tsTDkcJb91OGG_mD0NK8XrJw7eqk7SdVNsHQkIT3SSYSX3DbI8qLytGZHn0yQheAN3Hg0nmuY23_OQTpOweUsqNJxPOkaBLT6eE2GAG80FDDgImv4W4shGdRkdfYMXgL5n4uhKXJ0DIDFdA5eSo4CxM-hdssSe4rtNHHtH9F0aMFJHXYjM1uPumqa58aziLvS3cwZHEEPq3_8RQv0NFzB_j62kuHBThpYx_gLJudWNgyaOCpVXXxDxc9V1BPrnYcOhp56MHxcjV41Q5SSVWNXkZjwjzZRf9CyF0JdO1FRzOHJKv_ein8qPh2zWsqrqE_d16thyfHlHNuteCw7dcthVQR_2w5LkjdXedkRI3LyO_7O0gE5hHCErMOnlNMQDssWndTicx0-2V14Qtto_AVjOTyJcN-fBbNzxWcYifC798-FHcYrV1EnXdpAiyJYk27X-E93V31juuzN7WLM3SOvEfdEr_4z_-jhDYAtlrAcJi2Q-2k2A==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-01T18:50:00.000Z", "utc_arrival": "2023-06-01T16:50:00.000Z", "local_departure": "2023-06-01T15:35:00.000Z", "utc_departure": "2023-06-01T13:35:00.000Z"}, {"id": "0b770a224bfb0000cba453bb_0|0a220b774bfe0000f8408ba8_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 775.688741, "distance": 1975.87, "duration": {"departure": 12000, "return": 12900, "total": 24900}, "price": 235706.6063, "conversion": {"EUR": 617.022471, "HUF": 235706.6063}, "fare": {"adults": 117853.3, "children": 117853.3, "infants": 117853.3}, "bags_price": {"1": 109.704, "2": 219.422}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 2}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224bfb0000cba453bb_0", "combination_id": "0b770a224bfb0000cba453bb", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-04T10:15:00.000Z", "utc_arrival": "2023-04-04T08:15:00.000Z", "local_departure": "2023-04-04T06:55:00.000Z", "utc_departure": "2023-04-04T04:55:00.000Z"}, {"id": "0a220b774bfe0000f8408ba8_0", "combination_id": "0a220b774bfe0000f8408ba8", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "JKREG", "fare_category": "M", "fare_classes": "J", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-08T00:05:00.000Z", "utc_arrival": "2023-04-07T22:05:00.000Z", "local_departure": "2023-04-07T20:30:00.000Z", "utc_departure": "2023-04-07T18:30:00.000Z"}], "booking_token": "EzuZoTNoV5NcZAfdB7aBYyKQjorpUrF513ChYEeyCRcytmJaqNHt7oHBrjeDF8UY6VEkLMDeSas-q8z8JI9U563kcnYHnNFOlXWvy0U_PUqyLke4watd6CZpAlwaNEeYNPf1546avhDT7tE6vFy4T-8YE1yJZKCmb3YBRAo0v0zoaxWk2m7GfqQ205daS_VDmvT-x8eofL_9c-IXnV6Dmyn5hg5eevoazLHKxvIeIeRz5cg9xG_zfP-nD2NYlovWArjaytWmoU4g1avq6975RfpSq7MfMW6hbnf9vd9XEZyq8sw4IpeJIK94cIu7-Ha7ZtJ42uR_A6_yqhlLXE4rrvw3L9K_P6jNfoybNSIJ6mw5EAoJj1rbv3zxyPYUe89OSWxfESUngSkK88sUjvuzkRo_66cs0pfelzHgqjWRKq_KmqWQ13UTWPkB9bw_B3rVHSLdEraRBgc6xehztVps1VVDZEMF-M_laml5QdAbAKM8oeK0-3YAZMVQJrIqYqnGqJ6lIVL7JbkFmJEhP2cSW2p-uHAcMpRrkZgDCib2Z_Gbiavd86gY6S0BgVBUkKleCmts8oqbXpgmn2nkP8nfuDuXKBGTP99F3GLrTtktpWxC89rgV4We8dixT_VH76_krBQ_61FBQtjhw-Am9Qp6gwdMhMXz3tW-WrfntSlSH8HNfEWhBTBVCIT5Gf3K-3fT-LK_Br8zeQ7JGU8c1hzB-S__Rep3PdgKoqTkSEOqjdEhiusB02x_HTH6lFuIyKW4tAJ_XrsMndG6U_9Pn8GMWNw==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224bfb0000cba453bb_0%7C0a220b774bfe0000f8408ba8_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EzuZoTNoV5NcZAfdB7aBYyKQjorpUrF513ChYEeyCRcytmJaqNHt7oHBrjeDF8UY6VEkLMDeSas-q8z8JI9U563kcnYHnNFOlXWvy0U_PUqyLke4watd6CZpAlwaNEeYNPf1546avhDT7tE6vFy4T-8YE1yJZKCmb3YBRAo0v0zoaxWk2m7GfqQ205daS_VDmvT-x8eofL_9c-IXnV6Dmyn5hg5eevoazLHKxvIeIeRz5cg9xG_zfP-nD2NYlovWArjaytWmoU4g1avq6975RfpSq7MfMW6hbnf9vd9XEZyq8sw4IpeJIK94cIu7-Ha7ZtJ42uR_A6_yqhlLXE4rrvw3L9K_P6jNfoybNSIJ6mw5EAoJj1rbv3zxyPYUe89OSWxfESUngSkK88sUjvuzkRo_66cs0pfelzHgqjWRKq_KmqWQ13UTWPkB9bw_B3rVHSLdEraRBgc6xehztVps1VVDZEMF-M_laml5QdAbAKM8oeK0-3YAZMVQJrIqYqnGqJ6lIVL7JbkFmJEhP2cSW2p-uHAcMpRrkZgDCib2Z_Gbiavd86gY6S0BgVBUkKleCmts8oqbXpgmn2nkP8nfuDuXKBGTP99F3GLrTtktpWxC89rgV4We8dixT_VH76_krBQ_61FBQtjhw-Am9Qp6gwdMhMXz3tW-WrfntSlSH8HNfEWhBTBVCIT5Gf3K-3fT-LK_Br8zeQ7JGU8c1hzB-S__Rep3PdgKoqTkSEOqjdEhiusB02x_HTH6lFuIyKW4tAJ_XrsMndG6U_9Pn8GMWNw==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-04-04T10:15:00.000Z", "utc_arrival": "2023-04-04T08:15:00.000Z", "local_departure": "2023-04-04T06:55:00.000Z", "utc_departure": "2023-04-04T04:55:00.000Z"}, {"id": "0b770a224c25000076927589_0|0a220b774c280000bc72d948_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 773.004205, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 237227.7998, "conversion": {"EUR": 621.004585, "HUF": 237227.7998}, "fare": {"adults": 118613.9, "children": 118613.9, "infants": 118613.9}, "bags_price": {"1": 69.678, "2": 139.86}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 6}, "airlines": ["FR"], "route": [{"id": "0b770a224c25000076927589_0", "combination_id": "0b770a224c25000076927589", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-16T10:15:00.000Z", "utc_arrival": "2023-05-16T08:15:00.000Z", "local_departure": "2023-05-16T06:55:00.000Z", "utc_departure": "2023-05-16T04:55:00.000Z"}, {"id": "0a220b774c280000bc72d948_0", "combination_id": "0a220b774c280000bc72d948", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-19T18:00:00.000Z", "utc_arrival": "2023-05-19T16:00:00.000Z", "local_departure": "2023-05-19T14:50:00.000Z", "utc_departure": "2023-05-19T12:50:00.000Z"}], "booking_token": "ET-LdG61dP3zkG-QGFIhSyksHZekcPo54bJtHulcExiDJWDttQ61JfeScS_vhYM58sR6s8B79QmuW3ELb4NONM-lhAd_IXZxx5xGsWs6VM8S7cP-RapkqrNxYN0lwZZM1FDBQvDbYW9-69LuSte6VtnOl67Z104Fs5fG8RsrTEQOYxUS8zkpLcil5cTOrz8l_N8ekJuU-f1Fp00fXYopD7QJUWcaWsRwq8uacu5WvngfRQkASkIy8i1bkEtMv_yxW3Vh9LLFYaVdoOMpS7Qiq2pIywPhtdZUG6YVaT_Y2d6Nr5hbGIY_oLdZrcpH4pgu-mD8bRaOaP0A37W02_WDWMqDL-kUoyFTro981xNcvQqFoisazW5KJunXiRLPHmiwrhlMfpjH3KojJfCkfvbmgnYiLu9rrur3tg7I0c4mRL9y4cq0JucKT2us25VBff5Bb8TrVGnBaf3pA_tLjFZvyDe6SRrka0WuDs8Lfiu_0RvdV6nz1tWl7HR00-bGyLNltMDoNcajFKPzkZvYTgs5FsboMje5WA-eYXr3gKbQgL6krd1uIM-_gMf38ZHZD1JK_ALKR1oVkH8bvi-wu7TLE_O5RWChTfLR_MyOqArKSS0AXFWiFgdZ1tBmh0IARpkOJNy6-CoffD005d4eLkK85gjt-w_NcoD0l9HZUjJuu6BeGWUE0AzW37RbgNrfqFIt7Z_eZJPTAl3o-lTnO3KnIqCbpZWeU3Frp00PhWVRFv6w=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c25000076927589_0%7C0a220b774c280000bc72d948_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=ET-LdG61dP3zkG-QGFIhSyksHZekcPo54bJtHulcExiDJWDttQ61JfeScS_vhYM58sR6s8B79QmuW3ELb4NONM-lhAd_IXZxx5xGsWs6VM8S7cP-RapkqrNxYN0lwZZM1FDBQvDbYW9-69LuSte6VtnOl67Z104Fs5fG8RsrTEQOYxUS8zkpLcil5cTOrz8l_N8ekJuU-f1Fp00fXYopD7QJUWcaWsRwq8uacu5WvngfRQkASkIy8i1bkEtMv_yxW3Vh9LLFYaVdoOMpS7Qiq2pIywPhtdZUG6YVaT_Y2d6Nr5hbGIY_oLdZrcpH4pgu-mD8bRaOaP0A37W02_WDWMqDL-kUoyFTro981xNcvQqFoisazW5KJunXiRLPHmiwrhlMfpjH3KojJfCkfvbmgnYiLu9rrur3tg7I0c4mRL9y4cq0JucKT2us25VBff5Bb8TrVGnBaf3pA_tLjFZvyDe6SRrka0WuDs8Lfiu_0RvdV6nz1tWl7HR00-bGyLNltMDoNcajFKPzkZvYTgs5FsboMje5WA-eYXr3gKbQgL6krd1uIM-_gMf38ZHZD1JK_ALKR1oVkH8bvi-wu7TLE_O5RWChTfLR_MyOqArKSS0AXFWiFgdZ1tBmh0IARpkOJNy6-CoffD005d4eLkK85gjt-w_NcoD0l9HZUjJuu6BeGWUE0AzW37RbgNrfqFIt7Z_eZJPTAl3o-lTnO3KnIqCbpZWeU3Frp00PhWVRFv6w=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-16T10:15:00.000Z", "utc_arrival": "2023-05-16T08:15:00.000Z", "local_departure": "2023-05-16T06:55:00.000Z", "utc_departure": "2023-05-16T04:55:00.000Z"}, {"id": "0b770a224c19000028288b54_0|0a220b774c1c00004005581a_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 773.461945, "distance": 1975.87, "duration": {"departure": 11700, "return": 11700, "total": 23400}, "price": 237402.6595, "conversion": {"EUR": 621.462325, "HUF": 237402.6595}, "fare": {"adults": 118701.33, "children": 118701.33, "infants": 118701.33}, "bags_price": {"1": 83.3, "2": 176.4}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 158, "hold_height": 52, "hold_length": 78, "hold_weight": 20, "hold_width": 28, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 3, "personal_item_width": 15}, "availability": {"seats": 4}, "airlines": ["W6", "VY"], "route": [{"id": "0b770a224c19000028288b54_0", "combination_id": "0b770a224c19000028288b54", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "VY", "flight_no": 5193, "operating_carrier": "IB", "operating_flight_no": "3279", "fare_basis": "ZSBBHJA", "fare_category": "M", "fare_classes": "Z", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-04T18:50:00.000Z", "utc_arrival": "2023-05-04T16:50:00.000Z", "local_departure": "2023-05-04T15:35:00.000Z", "utc_departure": "2023-05-04T13:35:00.000Z"}, {"id": "0a220b774c1c00004005581a_0", "combination_id": "0a220b774c1c00004005581a", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "KREG", "fare_category": "M", "fare_classes": "K", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-07T21:05:00.000Z", "utc_arrival": "2023-05-07T19:05:00.000Z", "local_departure": "2023-05-07T17:50:00.000Z", "utc_departure": "2023-05-07T15:50:00.000Z"}], "booking_token": "EHuRBBgS37L2oo1As9L4wH6rCSZJT7ckFdSGmQQrDt7faHdV1mK2F5l-az2HbmWvO5cw8XgoOSih7cfSoFVyEXMW-0VHYP6AzGi5cESgsYAKDm_0xYMmd2N8vg7lvjA3BJ90u2Z70KPhlkoPmevWEte_DBzfupfrzZn9ISfSkSAiRzzwxLGRCw5Wx7i7iL7tHmcCLAktols06pFeI3SzV7HFbC2meOXsLBuJRGl5oWi03ez37jPoM3-G7cp2JEyV67htgue1S2kfxjf3oqYeOudOE-NQnZyBA4xNhDz7h_hEqIvLRnTghlUoA0FZ1fCF3xtIO5ehLVWafdQrPImWndmmrMP7h2ruuiwzb76EeyFYCeogzpN81x6ZmmTnei3WGDDEhuRNXWW_IwqenyGdx-guf2xUrlFpT_UOo6o-YZVL4Sk2C39VtA4HCGCyiC2uTNBLgfrBB3rJApCXmCsXV1Kdp938j_xIW8yVnPpbLjI85HxMJpcNMTMJosE9Qvl80xgYl5lp_lr6ufPWmaHO395x2HxJbq849LkmO57Oucx3yICS2FsuTGfe1YroWuGy5fB5TMUqGHT7WFo6dKG3QXrzfu0a6wC7o8wCeOLkXcAQOxbD3WOT80IPQD3_eTjNrBP1jU-N6F3-sk9uqvJmLz9QDPB2LsSzXMSc8Cj8OkXcFpUH86v8F_OQQnUJUhlJ61973hgm-deAy7_E6_uruHEDTvzGvq_LZE8DUShfg1ZwW7hXKhm5BC1SkLaSKcboHhzwDXdffiFTyjMAKogrT2XLYQlKArfk396TuwJWJ-yD-Xtwe0twzaMlF2-D0Cx2u", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c19000028288b54_0%7C0a220b774c1c00004005581a_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EHuRBBgS37L2oo1As9L4wH6rCSZJT7ckFdSGmQQrDt7faHdV1mK2F5l-az2HbmWvO5cw8XgoOSih7cfSoFVyEXMW-0VHYP6AzGi5cESgsYAKDm_0xYMmd2N8vg7lvjA3BJ90u2Z70KPhlkoPmevWEte_DBzfupfrzZn9ISfSkSAiRzzwxLGRCw5Wx7i7iL7tHmcCLAktols06pFeI3SzV7HFbC2meOXsLBuJRGl5oWi03ez37jPoM3-G7cp2JEyV67htgue1S2kfxjf3oqYeOudOE-NQnZyBA4xNhDz7h_hEqIvLRnTghlUoA0FZ1fCF3xtIO5ehLVWafdQrPImWndmmrMP7h2ruuiwzb76EeyFYCeogzpN81x6ZmmTnei3WGDDEhuRNXWW_IwqenyGdx-guf2xUrlFpT_UOo6o-YZVL4Sk2C39VtA4HCGCyiC2uTNBLgfrBB3rJApCXmCsXV1Kdp938j_xIW8yVnPpbLjI85HxMJpcNMTMJosE9Qvl80xgYl5lp_lr6ufPWmaHO395x2HxJbq849LkmO57Oucx3yICS2FsuTGfe1YroWuGy5fB5TMUqGHT7WFo6dKG3QXrzfu0a6wC7o8wCeOLkXcAQOxbD3WOT80IPQD3_eTjNrBP1jU-N6F3-sk9uqvJmLz9QDPB2LsSzXMSc8Cj8OkXcFpUH86v8F_OQQnUJUhlJ61973hgm-deAy7_E6_uruHEDTvzGvq_LZE8DUShfg1ZwW7hXKhm5BC1SkLaSKcboHhzwDXdffiFTyjMAKogrT2XLYQlKArfk396TuwJWJ-yD-Xtwe0twzaMlF2-D0Cx2u", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-04T18:50:00.000Z", "utc_arrival": "2023-05-04T16:50:00.000Z", "local_departure": "2023-05-04T15:35:00.000Z", "utc_departure": "2023-05-04T13:35:00.000Z"}, {"id": "0b770a224c180000fc3700cd_0|0a220b774c1c00004005581a_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 773.461945, "distance": 1975.87, "duration": {"departure": 11700, "return": 11700, "total": 23400}, "price": 237402.6595, "conversion": {"EUR": 621.462325, "HUF": 237402.6595}, "fare": {"adults": 118701.33, "children": 118701.33, "infants": 118701.33}, "bags_price": {"1": 83.3, "2": 176.4}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 158, "hold_height": 52, "hold_length": 78, "hold_weight": 20, "hold_width": 28, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 3, "personal_item_width": 15}, "availability": {"seats": 4}, "airlines": ["W6", "VY"], "route": [{"id": "0b770a224c180000fc3700cd_0", "combination_id": "0b770a224c180000fc3700cd", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "VY", "flight_no": 5193, "operating_carrier": "IB", "operating_flight_no": "3279", "fare_basis": "ZSBBHJA", "fare_category": "M", "fare_classes": "Z", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-03T18:50:00.000Z", "utc_arrival": "2023-05-03T16:50:00.000Z", "local_departure": "2023-05-03T15:35:00.000Z", "utc_departure": "2023-05-03T13:35:00.000Z"}, {"id": "0a220b774c1c00004005581a_0", "combination_id": "0a220b774c1c00004005581a", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "KREG", "fare_category": "M", "fare_classes": "K", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-07T21:05:00.000Z", "utc_arrival": "2023-05-07T19:05:00.000Z", "local_departure": "2023-05-07T17:50:00.000Z", "utc_departure": "2023-05-07T15:50:00.000Z"}], "booking_token": "EmcRi_rd8wSI1bp07GDC0uZQoGSahGB6QGuvwMvxkcHS2HJiACmls0Qd0qxScyzAeQmDgX1mU1rHd9eSiEWk2umAKNoZt7TUPsd2lNZ9Ike6-MED3gLaSr0PLomZbIAYW2AOydlt8P86MTO03rZGkZnphaH0CdQpP84-s9XL5ZtFTgazLf0UI5dvQ6GYfLlP08yG1jUcLNCY1_LEkMULlbQ7-OyZbYrwLb3o0FCZrGowrVXvn4AJkosOr15v48jqbY0r4HEXPsUyoHICI2Vh6DgNU3GbHo8Ks5w-UxAR-xVEBC9mqg86Z1LZo2LSo0iW96IjGmjubVgIyJ68dzw2pYTN_lTFbcXap01HL98Yr0G1RAVHYhbjd5eaMYunOCLK-zEus5WqVxTS5CA_Oej3zBESWXnlZ0s2ExIo3mp5pXcDuoyBTDbenfFxYxwlRa3Uz0elij2G8bqK7rMHJsCdT-pilSTOwm29M3fSGCexeWl4GrZ7r7uL1D_H4b4W5YMMqhLECnt9ZSwjiGlusoLFMpKymly_THj9rwIWLZ8A-pDf8If6IpyGs57hMB7BvlE3s7yg8rQqZrZbs7VNhYU21im0H2cA4f0355CYVFz9ysYe_bgWweb3rCphvYvfLJFmAhfOBvOjSbTVmscU1TRtBTLiBJsCOsrZ4nHwvFNZzzRiOyFlybsCJjGS3f7K0vSWqdS_hQziNfBzNSFtyzErQzE02B-ZPFY5tc5cZW2HBk7kAEAdL70I8QBtu8dXNAZJsF5PZQZ1J3IYjqy8MwPTjmcrpKRAsmrYyAZ_Ud08-WhE=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c180000fc3700cd_0%7C0a220b774c1c00004005581a_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EmcRi_rd8wSI1bp07GDC0uZQoGSahGB6QGuvwMvxkcHS2HJiACmls0Qd0qxScyzAeQmDgX1mU1rHd9eSiEWk2umAKNoZt7TUPsd2lNZ9Ike6-MED3gLaSr0PLomZbIAYW2AOydlt8P86MTO03rZGkZnphaH0CdQpP84-s9XL5ZtFTgazLf0UI5dvQ6GYfLlP08yG1jUcLNCY1_LEkMULlbQ7-OyZbYrwLb3o0FCZrGowrVXvn4AJkosOr15v48jqbY0r4HEXPsUyoHICI2Vh6DgNU3GbHo8Ks5w-UxAR-xVEBC9mqg86Z1LZo2LSo0iW96IjGmjubVgIyJ68dzw2pYTN_lTFbcXap01HL98Yr0G1RAVHYhbjd5eaMYunOCLK-zEus5WqVxTS5CA_Oej3zBESWXnlZ0s2ExIo3mp5pXcDuoyBTDbenfFxYxwlRa3Uz0elij2G8bqK7rMHJsCdT-pilSTOwm29M3fSGCexeWl4GrZ7r7uL1D_H4b4W5YMMqhLECnt9ZSwjiGlusoLFMpKymly_THj9rwIWLZ8A-pDf8If6IpyGs57hMB7BvlE3s7yg8rQqZrZbs7VNhYU21im0H2cA4f0355CYVFz9ysYe_bgWweb3rCphvYvfLJFmAhfOBvOjSbTVmscU1TRtBTLiBJsCOsrZ4nHwvFNZzzRiOyFlybsCJjGS3f7K0vSWqdS_hQziNfBzNSFtyzErQzE02B-ZPFY5tc5cZW2HBk7kAEAdL70I8QBtu8dXNAZJsF5PZQZ1J3IYjqy8MwPTjmcrpKRAsmrYyAZ_Ud08-WhE=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-03T18:50:00.000Z", "utc_arrival": "2023-05-03T16:50:00.000Z", "local_departure": "2023-05-03T15:35:00.000Z", "utc_departure": "2023-05-03T13:35:00.000Z"}, {"id": "0b770a224c4a0000c81c2b63_0|0a220b774c4d0000e5d40dae_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 773.561198, "distance": 1975.87, "duration": {"departure": 11700, "return": 11700, "total": 23400}, "price": 237440.5748, "conversion": {"EUR": 621.561578, "HUF": 237440.5748}, "fare": {"adults": 118720.29, "children": 118720.29, "infants": 118720.29}, "bags_price": {"1": 97.118, "2": 204.036}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 158, "hold_height": 52, "hold_length": 78, "hold_weight": 20, "hold_width": 28, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 3, "personal_item_width": 15}, "availability": {"seats": 4}, "airlines": ["W6", "IB"], "route": [{"id": "0b770a224c4a0000c81c2b63_0", "combination_id": "0b770a224c4a0000c81c2b63", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "IB", "flight_no": 3279, "operating_carrier": "IB", "operating_flight_no": "3279", "fare_basis": "ODNNAOB4", "fare_category": "M", "fare_classes": "O", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-22T18:50:00.000Z", "utc_arrival": "2023-06-22T16:50:00.000Z", "local_departure": "2023-06-22T15:35:00.000Z", "utc_departure": "2023-06-22T13:35:00.000Z"}, {"id": "0a220b774c4d0000e5d40dae_0", "combination_id": "0a220b774c4d0000e5d40dae", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-25T21:05:00.000Z", "utc_arrival": "2023-06-25T19:05:00.000Z", "local_departure": "2023-06-25T17:50:00.000Z", "utc_departure": "2023-06-25T15:50:00.000Z"}], "booking_token": "EIlTE16Nx35SUs_Dizl9jR9S4Vc41M8IHL1dzGcGEjNN4pvISukQs82kdUaXMVqM_T5NL9udKxjFqZXUa7EWepYUDmLvUp5OWpjr0eu-jd72xP2y6unKnhKRWcOAe8CcqzIYUJ3qjSO96ZnyYqUDfFBOSLXFRqL0PKARiPzUzVpJvNrONpDhArX52yd4eE-JFQK2T1Suh89Xq61hvfTSSwo97AuUo2UmHHfysXPaIofQi6un3y6aTiJwUAU91m8UVO198J6KcRgfM0fsvq_pZ-SbIY1TxOO3r6uN4RwOM0N6fUuW-6K0rCPAfl5LWtWdMmhdxlCQaDG-qGgBZcDGZEiLHJDPSldMwmvt3mV_yH4cmEM8U-lHgmGrVWB_OIq1pBf1pCbc-BV4IDzctTKD4szyyTuVtErZRvgHKx4yxjTUctuTH4AI3afD3K3KPqIJwBgOUIpcidTPlJ2ioEd45ZrM8FKGf_IHHXAiQS2EaS_plOW_4OBHNbg64e8gEgn4Xrw49dVmr50VRPyKJrJBy7BPmIa49j9ti-qCY-9uZ6ztPo251vflZEr3wPXBhcbHYplXdb65zyl4nDsBqBm9VNLjeMaMp7I450TOBnRF2v81KuTYd7ISMJc2cXrU2LzkXYOJSqGPyrzyFBW08hl913MXE-AyoO2pM62MMGjjD8vXVk6O81gta9SrAZtmQ1pcVULxxKX8l00k1Ps-ovvOunJI27ziwfnFN1uu8A2OkZHVGKU05VxjDs_-EJyyoi_F6OFWkqe2o8ZTWrRy0ZX_Yesn7ATBcW5Pdgb1pFKaubzor--FLfvcnh2n-rKoZOGdL", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c4a0000c81c2b63_0%7C0a220b774c4d0000e5d40dae_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EIlTE16Nx35SUs_Dizl9jR9S4Vc41M8IHL1dzGcGEjNN4pvISukQs82kdUaXMVqM_T5NL9udKxjFqZXUa7EWepYUDmLvUp5OWpjr0eu-jd72xP2y6unKnhKRWcOAe8CcqzIYUJ3qjSO96ZnyYqUDfFBOSLXFRqL0PKARiPzUzVpJvNrONpDhArX52yd4eE-JFQK2T1Suh89Xq61hvfTSSwo97AuUo2UmHHfysXPaIofQi6un3y6aTiJwUAU91m8UVO198J6KcRgfM0fsvq_pZ-SbIY1TxOO3r6uN4RwOM0N6fUuW-6K0rCPAfl5LWtWdMmhdxlCQaDG-qGgBZcDGZEiLHJDPSldMwmvt3mV_yH4cmEM8U-lHgmGrVWB_OIq1pBf1pCbc-BV4IDzctTKD4szyyTuVtErZRvgHKx4yxjTUctuTH4AI3afD3K3KPqIJwBgOUIpcidTPlJ2ioEd45ZrM8FKGf_IHHXAiQS2EaS_plOW_4OBHNbg64e8gEgn4Xrw49dVmr50VRPyKJrJBy7BPmIa49j9ti-qCY-9uZ6ztPo251vflZEr3wPXBhcbHYplXdb65zyl4nDsBqBm9VNLjeMaMp7I450TOBnRF2v81KuTYd7ISMJc2cXrU2LzkXYOJSqGPyrzyFBW08hl913MXE-AyoO2pM62MMGjjD8vXVk6O81gta9SrAZtmQ1pcVULxxKX8l00k1Ps-ovvOunJI27ziwfnFN1uu8A2OkZHVGKU05VxjDs_-EJyyoi_F6OFWkqe2o8ZTWrRy0ZX_Yesn7ATBcW5Pdgb1pFKaubzor--FLfvcnh2n-rKoZOGdL", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-22T18:50:00.000Z", "utc_arrival": "2023-06-22T16:50:00.000Z", "local_departure": "2023-06-22T15:35:00.000Z", "utc_departure": "2023-06-22T13:35:00.000Z"}, {"id": "0b770a224be8000084d26d37_0|0a220b774beb0000ffe2d784_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 776.504371, "distance": 1975.87, "duration": {"departure": 12000, "return": 11700, "total": 23700}, "price": 238055.5453, "conversion": {"EUR": 623.171421, "HUF": 238055.5453}, "fare": {"adults": 119027.77, "children": 119027.77, "infants": 119027.77}, "bags_price": {"1": 104.062, "2": 208.138}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 439, "hold_height": 149, "hold_length": 171, "hold_weight": 20, "hold_width": 119, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 3}, "airlines": ["W6"], "route": [{"id": "0b770a224be8000084d26d37_0", "combination_id": "0b770a224be8000084d26d37", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "JKREG", "fare_category": "M", "fare_classes": "J", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-03-16T19:40:00.000Z", "utc_arrival": "2023-03-16T18:40:00.000Z", "local_departure": "2023-03-16T16:20:00.000Z", "utc_departure": "2023-03-16T15:20:00.000Z"}, {"id": "0a220b774beb0000ffe2d784_0", "combination_id": "0a220b774beb0000ffe2d784", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "HREG", "fare_category": "M", "fare_classes": "H", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-03-19T21:45:00.000Z", "utc_arrival": "2023-03-19T20:45:00.000Z", "local_departure": "2023-03-19T18:30:00.000Z", "utc_departure": "2023-03-19T17:30:00.000Z"}], "booking_token": "EPVXtkUsg_087Ll7uI12oC48smwD22Ik6Xp6nyZPxZdHGHsHoRwv7stXIIm5EfEbQ6q_0ZREtDSy3gvAliwUrqq3ueIDclUduiuGycvJNP79Admyvi-nmRmfJ3b23uqntiod79x_ubawzcRtY1b4ipx3sXK5JG8nabu6CzxKKQGeQ4MukxoVTIIXT0SSdzW-Ug6w8QdgmdiFN_U1DIHhs66lEj1BkSaWeUfPZXESecy2VScf7X2LkTtTkO8VewkWWBgPjwK2m6A0trYMtwDBTkPAW4wtouNOyZc1YQoJ2b7lkEIu3yrF1m3jkxdECQgspC9f4WsZK4qEUBXh5OF9smcqPV-Fusiutnd99xIQzLoW1LFtzm8qxB18YIzeaIzODQFioVjREUZnCA-ktulVlzls82XOR_eG1cOUKy4AgogTus07-Marqyi5FfbfM7WWHPoE0HE_ZdQwgm_xgTAfx3mVMSAIOAwgwBBWHZyOVY4A9xeKmQL5nMI1_SvqMq2dFEsi6BvoID28CzE6fspEg-5ozeCu4bc161AmuMJQICTH3DNaYi0hHzTQ5Tc1tLm6ODY2UgozwoKy85mCgK1AaLPx0AKm3UvxCyJ3_N63KTeSEn0SRBHkTJ3QyDo8FpvJhpNUckyoJLW6nmRQ6lEfUMiJ-oZQkU3V4kqlruQbhs8XKF4ErzrwWpFEsYya3dEVDpMBH3GKziyDOMK92ipPr0g5PE_8aCkshDMgb1OHhkn2Lk5Cr7GBvuBnwLplgdsK1TUywW8k-KrYWAk1s9N7w99OxOQB7AMsYumhs2zJLVPo=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224be8000084d26d37_0%7C0a220b774beb0000ffe2d784_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EPVXtkUsg_087Ll7uI12oC48smwD22Ik6Xp6nyZPxZdHGHsHoRwv7stXIIm5EfEbQ6q_0ZREtDSy3gvAliwUrqq3ueIDclUduiuGycvJNP79Admyvi-nmRmfJ3b23uqntiod79x_ubawzcRtY1b4ipx3sXK5JG8nabu6CzxKKQGeQ4MukxoVTIIXT0SSdzW-Ug6w8QdgmdiFN_U1DIHhs66lEj1BkSaWeUfPZXESecy2VScf7X2LkTtTkO8VewkWWBgPjwK2m6A0trYMtwDBTkPAW4wtouNOyZc1YQoJ2b7lkEIu3yrF1m3jkxdECQgspC9f4WsZK4qEUBXh5OF9smcqPV-Fusiutnd99xIQzLoW1LFtzm8qxB18YIzeaIzODQFioVjREUZnCA-ktulVlzls82XOR_eG1cOUKy4AgogTus07-Marqyi5FfbfM7WWHPoE0HE_ZdQwgm_xgTAfx3mVMSAIOAwgwBBWHZyOVY4A9xeKmQL5nMI1_SvqMq2dFEsi6BvoID28CzE6fspEg-5ozeCu4bc161AmuMJQICTH3DNaYi0hHzTQ5Tc1tLm6ODY2UgozwoKy85mCgK1AaLPx0AKm3UvxCyJ3_N63KTeSEn0SRBHkTJ3QyDo8FpvJhpNUckyoJLW6nmRQ6lEfUMiJ-oZQkU3V4kqlruQbhs8XKF4ErzrwWpFEsYya3dEVDpMBH3GKziyDOMK92ipPr0g5PE_8aCkshDMgb1OHhkn2Lk5Cr7GBvuBnwLplgdsK1TUywW8k-KrYWAk1s9N7w99OxOQB7AMsYumhs2zJLVPo=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-03-16T19:40:00.000Z", "utc_arrival": "2023-03-16T18:40:00.000Z", "local_departure": "2023-03-16T16:20:00.000Z", "utc_departure": "2023-03-16T15:20:00.000Z"}, {"id": "0b770a224c0c00004f039f60_0|0a220b774c0f00005b6aa57a_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 776.991763, "distance": 1975.87, "duration": {"departure": 12000, "return": 11700, "total": 23700}, "price": 238241.7322, "conversion": {"EUR": 623.658813, "HUF": 238241.7322}, "fare": {"adults": 119120.87, "children": 121941.23, "infants": 121941.23}, "bags_price": {"1": 64.554, "2": 129.094}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 6}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224c0c00004f039f60_0", "combination_id": "0b770a224c0c00004f039f60", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-21T21:45:00.000Z", "utc_arrival": "2023-04-21T19:45:00.000Z", "local_departure": "2023-04-21T18:25:00.000Z", "utc_departure": "2023-04-21T16:25:00.000Z"}, {"id": "0a220b774c0f00005b6aa57a_0", "combination_id": "0a220b774c0f00005b6aa57a", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IJREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-24T23:45:00.000Z", "utc_arrival": "2023-04-24T21:45:00.000Z", "local_departure": "2023-04-24T20:30:00.000Z", "utc_departure": "2023-04-24T18:30:00.000Z"}], "booking_token": "EcHBbrKgXe-JJDKmcfB6Ox2-HqNq2Ec-0yU7bJVsby_zq9SP_C6LeKzI0K4tE5hMHNmz5CkyrY2ROtK_ws2OldypKlSCmwh0cH49PDBIF-Iild_Nxtg12msF2RxT5AmZT7BpP_ckbm8XBCtNAFwIYgubBXh_VegvVsGgQbyaDVxaxEjpBUPUQ695crEiws1aHDsb1EHkbxhVFD60C-DiElDEI0RJzAlK181dYWdSpwH_k3iST1iIOQbxr5BShz_UwSHXavU4y_2RkiCkyGGD2UtYnL8nWiUEtPaJlo0yLKIVCCW2G2TByppCxqKpMzUv9eWgRDTkqMesGCAEFFNlc-XFbL944e3tSYt4pqRdDZqINMOIysD5eZTpjS2SosJGnU2N39uZ-GCr-OH0jKuxZ_NUgRG2OJkRWPR6O-zh1tBdto9IxBXBE455TJrfGxvGuXrpCwI7KwflzRAvlcwCigV45q95IT4dzpRqlndF3cA0zdCJrKVq2E6kfqImnTI_YLWuq8c0Qc_pGi4SdjdStxq9DHyje1lFbtEEN00Zu33CiNcp49p3T5In_HK7IZo1DodrRuZqC0JljTODCKVn2ZjEoMKolUzNzXiKP9Xd8cy_V_iSwdoIxEAdLOm3tdNsa7wIYVxtcaVAKVXIo_KdaFswQwUUgjtXqZEUbuJqHlw1Mn4nNdOPfF98y_aMzcwlyX4YMP2H5_6653KDoMKbM_0D7G_ngeJ7IfxY-dS1UDLHZVaZKKdWIEVq5PJ2GUYqbQLFyKy_I_Trp2ca5l1gByKlmy6_iaqVelQZ0vOtHkEk=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c0c00004f039f60_0%7C0a220b774c0f00005b6aa57a_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EcHBbrKgXe-JJDKmcfB6Ox2-HqNq2Ec-0yU7bJVsby_zq9SP_C6LeKzI0K4tE5hMHNmz5CkyrY2ROtK_ws2OldypKlSCmwh0cH49PDBIF-Iild_Nxtg12msF2RxT5AmZT7BpP_ckbm8XBCtNAFwIYgubBXh_VegvVsGgQbyaDVxaxEjpBUPUQ695crEiws1aHDsb1EHkbxhVFD60C-DiElDEI0RJzAlK181dYWdSpwH_k3iST1iIOQbxr5BShz_UwSHXavU4y_2RkiCkyGGD2UtYnL8nWiUEtPaJlo0yLKIVCCW2G2TByppCxqKpMzUv9eWgRDTkqMesGCAEFFNlc-XFbL944e3tSYt4pqRdDZqINMOIysD5eZTpjS2SosJGnU2N39uZ-GCr-OH0jKuxZ_NUgRG2OJkRWPR6O-zh1tBdto9IxBXBE455TJrfGxvGuXrpCwI7KwflzRAvlcwCigV45q95IT4dzpRqlndF3cA0zdCJrKVq2E6kfqImnTI_YLWuq8c0Qc_pGi4SdjdStxq9DHyje1lFbtEEN00Zu33CiNcp49p3T5In_HK7IZo1DodrRuZqC0JljTODCKVn2ZjEoMKolUzNzXiKP9Xd8cy_V_iSwdoIxEAdLOm3tdNsa7wIYVxtcaVAKVXIo_KdaFswQwUUgjtXqZEUbuJqHlw1Mn4nNdOPfF98y_aMzcwlyX4YMP2H5_6653KDoMKbM_0D7G_ngeJ7IfxY-dS1UDLHZVaZKKdWIEVq5PJ2GUYqbQLFyKy_I_Trp2ca5l1gByKlmy6_iaqVelQZ0vOtHkEk=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-04-21T21:45:00.000Z", "utc_arrival": "2023-04-21T19:45:00.000Z", "local_departure": "2023-04-21T18:25:00.000Z", "utc_departure": "2023-04-21T16:25:00.000Z"}, {"id": "0b770a224c1e00003e2ba34c_0|0a220b774c2100009e582914_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 775.848955, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 238314.5128, "conversion": {"EUR": 623.849335, "HUF": 238314.5128}, "fare": {"adults": 119157.26, "children": 119157.26, "infants": 119157.26}, "bags_price": {"1": 71.75, "2": 143.5}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 6}, "airlines": ["FR"], "route": [{"id": "0b770a224c1e00003e2ba34c_0", "combination_id": "0b770a224c1e00003e2ba34c", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-09T10:15:00.000Z", "utc_arrival": "2023-05-09T08:15:00.000Z", "local_departure": "2023-05-09T06:55:00.000Z", "utc_departure": "2023-05-09T04:55:00.000Z"}, {"id": "0a220b774c2100009e582914_0", "combination_id": "0a220b774c2100009e582914", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-12T18:00:00.000Z", "utc_arrival": "2023-05-12T16:00:00.000Z", "local_departure": "2023-05-12T14:50:00.000Z", "utc_departure": "2023-05-12T12:50:00.000Z"}], "booking_token": "EUgsHK-jk4hxnSfD4kI9FP6SzaycstXQxzEnhY5-ol2XY0-jZjvku3IQOQFxpY7mEP_w2vWkSyp7msQBFPfCzzgjzU52E3dQjmhx06hCN5eb_HgR4i8bH0HxEpB6gZG9T2PZIkOnh_HkOxB4jiWuBWLhDSygMIhuofjPNOo6qaxt9-GmNGtgTYmyx8chaPbdnTAbsr0AocDAEaiJT45OkTE-N6e5MnCImYNCqNkpmRsCq-5iVnYmpKaDWoC8bsknf4OXYW78g_wjAmlY4x-QGrw6YSy0i9LbgLlALcGASq-YPZ38tGMA4-uRAODj-OkqLzVJ1RGTAranZ_5A5qLaCQgU_Oy9rJS8qIWNJVrIvU5IWIGoXail6lOEqKH9WE6qt4DLNdM8_by8DsuDzqrWIbJyG2TsDsq3XzAH5rdYb-ZZZDLun0Dg_vszJ8GvVt8bapta6d1TSpKfBjK9ARrWg7bMLWrs-0TmQkuNLfHs-caxLAE1zRmplZdtq1opHAesmmyV71qW7OfSxI3owLfQfQZOtp9NWFs86qhakFQfgpsVPi2jcIfqJ5GX8YxdXIg-ZpiTo1Ym3ipriqfqE09dolGEAG1xbmO__j0CX5mYbx0AhN3NJF5kPv1TEnQ9FBKLUl1abCjmeMFoHBe1tCkLEPiO1CeFhsH82_ZsYGM_8Z2pP_Z5GH_G1BQQhH4a1iq5s3NLh8a8NcDI9VSvsDH_hVgYcLDi1NUZQyEw1HyVLabg=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c1e00003e2ba34c_0%7C0a220b774c2100009e582914_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EUgsHK-jk4hxnSfD4kI9FP6SzaycstXQxzEnhY5-ol2XY0-jZjvku3IQOQFxpY7mEP_w2vWkSyp7msQBFPfCzzgjzU52E3dQjmhx06hCN5eb_HgR4i8bH0HxEpB6gZG9T2PZIkOnh_HkOxB4jiWuBWLhDSygMIhuofjPNOo6qaxt9-GmNGtgTYmyx8chaPbdnTAbsr0AocDAEaiJT45OkTE-N6e5MnCImYNCqNkpmRsCq-5iVnYmpKaDWoC8bsknf4OXYW78g_wjAmlY4x-QGrw6YSy0i9LbgLlALcGASq-YPZ38tGMA4-uRAODj-OkqLzVJ1RGTAranZ_5A5qLaCQgU_Oy9rJS8qIWNJVrIvU5IWIGoXail6lOEqKH9WE6qt4DLNdM8_by8DsuDzqrWIbJyG2TsDsq3XzAH5rdYb-ZZZDLun0Dg_vszJ8GvVt8bapta6d1TSpKfBjK9ARrWg7bMLWrs-0TmQkuNLfHs-caxLAE1zRmplZdtq1opHAesmmyV71qW7OfSxI3owLfQfQZOtp9NWFs86qhakFQfgpsVPi2jcIfqJ5GX8YxdXIg-ZpiTo1Ym3ipriqfqE09dolGEAG1xbmO__j0CX5mYbx0AhN3NJF5kPv1TEnQ9FBKLUl1abCjmeMFoHBe1tCkLEPiO1CeFhsH82_ZsYGM_8Z2pP_Z5GH_G1BQQhH4a1iq5s3NLh8a8NcDI9VSvsDH_hVgYcLDi1NUZQyEw1HyVLabg=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-09T10:15:00.000Z", "utc_arrival": "2023-05-09T08:15:00.000Z", "local_departure": "2023-05-09T06:55:00.000Z", "utc_departure": "2023-05-09T04:55:00.000Z"}, {"id": "0b770a224c490000960764e7_0|0a220b774c4d0000e5d40dae_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 776.990459, "distance": 1975.87, "duration": {"departure": 11700, "return": 11700, "total": 23400}, "price": 238750.5748, "conversion": {"EUR": 624.990839, "HUF": 238750.5748}, "fare": {"adults": 119375.29, "children": 125111.86, "infants": 125111.86}, "bags_price": {"1": 97.118, "2": 204.036}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 158, "hold_height": 52, "hold_length": 78, "hold_weight": 20, "hold_width": 28, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 3, "personal_item_width": 15}, "availability": {"seats": 4}, "airlines": ["W6", "IB"], "route": [{"id": "0b770a224c490000960764e7_0", "combination_id": "0b770a224c490000960764e7", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "IB", "flight_no": 3279, "operating_carrier": "IB", "operating_flight_no": "3279", "fare_basis": "QDNNAOB4", "fare_category": "M", "fare_classes": "Q", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-21T18:50:00.000Z", "utc_arrival": "2023-06-21T16:50:00.000Z", "local_departure": "2023-06-21T15:35:00.000Z", "utc_departure": "2023-06-21T13:35:00.000Z"}, {"id": "0a220b774c4d0000e5d40dae_0", "combination_id": "0a220b774c4d0000e5d40dae", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-25T21:05:00.000Z", "utc_arrival": "2023-06-25T19:05:00.000Z", "local_departure": "2023-06-25T17:50:00.000Z", "utc_departure": "2023-06-25T15:50:00.000Z"}], "booking_token": "EDVOHt48_crNprsE6AP-qh3Qd1oqwjA62qKWP15S99dko15sU5LEJ-XBhZaJ1UZHk3HNQYxPEP1Zje2yHi8bhXMDKe-rlKRn7yNWsGcGVAqnEoxrAYBNXkuvVTggXYjHQISWNflW1gStDd8EwffOdd3fojEq83jYHfeo9YDfloBtnh7ZKFSI4ZvmLuVs0cFUDFfEEtFtEQrsvxgDQt_WmAi__LbNr3SntR1wTVlDOMkp3OOC3YhFEZWMfdkp3YfdXoOr3WEuya2Z5xKvSu0fAYrXz7MbuXgEb4ztkXzYZOAPa6YOtN4wt8GKhg-27n5S5sQKoEOnv6nu4OzxxP0GzJWhc7ALA8JQ5EnRR334Rw9d8-QrwcebYDkbASPw29a-vWZln2JOFTsuFkiYls8YC1lOu96URF7y33bmeRtJn5icOwDmFXZzxmvU0Vc3ClBCgRqdFk95FRvjxMDPYhYrtTXlMV0vWlW23R35YwqbRz7RUjkxI8DjsS7YwBJ1vZyt-ejDscnWeBb4JzsKSVTi5JhtAn5LTG36fxkanNeZfETyUOdQUdXGUKnF7e461Peshcw6TlPgk2iVVrutnY682YqN5Qp6rRWTVf13_8PhvuLdprZm5hVXnZ8ziiodGpuGF7ddqlkkl7qVcNFppAQ-QAt4JvfAcWLFEZajwd0LeygBviDYxPev981ce3olZ7Z0tRPFVHbPxQ6PRNi_Nm7vvcYAPmlAoAUTHY3W1UGOJNx9d9Ny7NhvkpClm3CBTgJQNWthUiYqhHWNtl15SRqOlSiqXo5zRkkJc1i0M9S_Ta8E=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c490000960764e7_0%7C0a220b774c4d0000e5d40dae_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EDVOHt48_crNprsE6AP-qh3Qd1oqwjA62qKWP15S99dko15sU5LEJ-XBhZaJ1UZHk3HNQYxPEP1Zje2yHi8bhXMDKe-rlKRn7yNWsGcGVAqnEoxrAYBNXkuvVTggXYjHQISWNflW1gStDd8EwffOdd3fojEq83jYHfeo9YDfloBtnh7ZKFSI4ZvmLuVs0cFUDFfEEtFtEQrsvxgDQt_WmAi__LbNr3SntR1wTVlDOMkp3OOC3YhFEZWMfdkp3YfdXoOr3WEuya2Z5xKvSu0fAYrXz7MbuXgEb4ztkXzYZOAPa6YOtN4wt8GKhg-27n5S5sQKoEOnv6nu4OzxxP0GzJWhc7ALA8JQ5EnRR334Rw9d8-QrwcebYDkbASPw29a-vWZln2JOFTsuFkiYls8YC1lOu96URF7y33bmeRtJn5icOwDmFXZzxmvU0Vc3ClBCgRqdFk95FRvjxMDPYhYrtTXlMV0vWlW23R35YwqbRz7RUjkxI8DjsS7YwBJ1vZyt-ejDscnWeBb4JzsKSVTi5JhtAn5LTG36fxkanNeZfETyUOdQUdXGUKnF7e461Peshcw6TlPgk2iVVrutnY682YqN5Qp6rRWTVf13_8PhvuLdprZm5hVXnZ8ziiodGpuGF7ddqlkkl7qVcNFppAQ-QAt4JvfAcWLFEZajwd0LeygBviDYxPev981ce3olZ7Z0tRPFVHbPxQ6PRNi_Nm7vvcYAPmlAoAUTHY3W1UGOJNx9d9Ny7NhvkpClm3CBTgJQNWthUiYqhHWNtl15SRqOlSiqXo5zRkkJc1i0M9S_Ta8E=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-21T18:50:00.000Z", "utc_arrival": "2023-06-21T16:50:00.000Z", "local_departure": "2023-06-21T15:35:00.000Z", "utc_departure": "2023-06-21T13:35:00.000Z"}, {"id": "0b770a224be800009070ff04_0|0a220b774beb0000ffe2d784_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 781.530168, "distance": 1975.87, "duration": {"departure": 12000, "return": 11700, "total": 23700}, "price": 239975.4325, "conversion": {"EUR": 628.197218, "HUF": 239975.4325}, "fare": {"adults": 119987.72, "children": 124614.99, "infants": 124614.99}, "bags_price": {"1": 88.69, "2": 177.366}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 6}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224be800009070ff04_0", "combination_id": "0b770a224be800009070ff04", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-03-16T13:40:00.000Z", "utc_arrival": "2023-03-16T12:40:00.000Z", "local_departure": "2023-03-16T10:20:00.000Z", "utc_departure": "2023-03-16T09:20:00.000Z"}, {"id": "0a220b774beb0000ffe2d784_0", "combination_id": "0a220b774beb0000ffe2d784", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "HREG", "fare_category": "M", "fare_classes": "H", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-03-19T21:45:00.000Z", "utc_arrival": "2023-03-19T20:45:00.000Z", "local_departure": "2023-03-19T18:30:00.000Z", "utc_departure": "2023-03-19T17:30:00.000Z"}], "booking_token": "EA7hBDN_TW8Au9tf9fmx6yEsX4fy3apUG1jv1ScHWdrTsO6FTxfraqqgA0InWQ9KxE4Cz9Kjjjr8wq3nd9KwiE3mGl84CV_oP_8ZNRyZZ-LGaWC5Y5z1IsrLfLAGgdM9zzTgOXhzDLSRv78D8Ba9glxOtFF5hTfFBaSJ-zTvH385zsHcF1xBNObnCipT5HD26-a33kTmSnfKLHmR_IJ7cRCQo-qcPNnnBMTLNlW8vCCVB8IrM5fYjmrSd2PhoqGTb9jAm-gYVu2jdhviGXoVyGTq3lkT-efn-Dlhucoaoc5hD9evZO_I4szO_nb0U0kIwMzHy0t42iLYuzh27PEO5q4EYNyQ2GBotXzqp5dfobBKZTCCn8DAWWkFcBDXu0exx_ArF6q4VCRQ_lPUKN9PUNxMU6F7FfHSQDwkAP0xy7W8NFCMQRelbSTo6cXv8ppGflsfzFRcroJKosYnJLUyOg9_kDzgO5VJq2i6iGwbaI-F8CyoqhzJXn5Oej7uUZzuMCVB4ko0wqeIFj6CE2e37O7maZHABZdfByD80lpc01KeiSRgu0R9hSWqhggOMJwaX5KOKtKHxpTbAjluqxnQyYjqKlosB-msrvmzZHS2TY2ZTq_fU5kSlQw94q06byJQmLnCz1jDHEIsrop7acTLAqEWrHCiOGdQO7mdarIKx-Qx9Juc5uFoxfXhgBlF8qvnz8JwVcI2RjekChdM0Q7DSaab7j1MJbdUUxg-MIXJ7NJwCpGeuHSNYqv3zB_39QRINCXuUeWDLJVzPHO0RQ7To6lZL-R3h3p5aNTjv2EQdhyk=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224be800009070ff04_0%7C0a220b774beb0000ffe2d784_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EA7hBDN_TW8Au9tf9fmx6yEsX4fy3apUG1jv1ScHWdrTsO6FTxfraqqgA0InWQ9KxE4Cz9Kjjjr8wq3nd9KwiE3mGl84CV_oP_8ZNRyZZ-LGaWC5Y5z1IsrLfLAGgdM9zzTgOXhzDLSRv78D8Ba9glxOtFF5hTfFBaSJ-zTvH385zsHcF1xBNObnCipT5HD26-a33kTmSnfKLHmR_IJ7cRCQo-qcPNnnBMTLNlW8vCCVB8IrM5fYjmrSd2PhoqGTb9jAm-gYVu2jdhviGXoVyGTq3lkT-efn-Dlhucoaoc5hD9evZO_I4szO_nb0U0kIwMzHy0t42iLYuzh27PEO5q4EYNyQ2GBotXzqp5dfobBKZTCCn8DAWWkFcBDXu0exx_ArF6q4VCRQ_lPUKN9PUNxMU6F7FfHSQDwkAP0xy7W8NFCMQRelbSTo6cXv8ppGflsfzFRcroJKosYnJLUyOg9_kDzgO5VJq2i6iGwbaI-F8CyoqhzJXn5Oej7uUZzuMCVB4ko0wqeIFj6CE2e37O7maZHABZdfByD80lpc01KeiSRgu0R9hSWqhggOMJwaX5KOKtKHxpTbAjluqxnQyYjqKlosB-msrvmzZHS2TY2ZTq_fU5kSlQw94q06byJQmLnCz1jDHEIsrop7acTLAqEWrHCiOGdQO7mdarIKx-Qx9Juc5uFoxfXhgBlF8qvnz8JwVcI2RjekChdM0Q7DSaab7j1MJbdUUxg-MIXJ7NJwCpGeuHSNYqv3zB_39QRINCXuUeWDLJVzPHO0RQ7To6lZL-R3h3p5aNTjv2EQdhyk=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-03-16T13:40:00.000Z", "utc_arrival": "2023-03-16T12:40:00.000Z", "local_departure": "2023-03-16T10:20:00.000Z", "utc_departure": "2023-03-16T09:20:00.000Z"}, {"id": "0b770a224bfb0000cba453bb_0|0a220b774bfe000002ec78b7_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 780.717139, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 240174.1909, "conversion": {"EUR": 628.717519, "HUF": 240174.1909}, "fare": {"adults": 120087.1, "children": 120087.1, "infants": 120087.1}, "bags_price": {"1": 108.318, "2": 216.664}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 4}, "airlines": ["FR"], "route": [{"id": "0b770a224bfb0000cba453bb_0", "combination_id": "0b770a224bfb0000cba453bb", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-04T10:15:00.000Z", "utc_arrival": "2023-04-04T08:15:00.000Z", "local_departure": "2023-04-04T06:55:00.000Z", "utc_departure": "2023-04-04T04:55:00.000Z"}, {"id": "0a220b774bfe000002ec78b7_0", "combination_id": "0a220b774bfe000002ec78b7", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-07T18:00:00.000Z", "utc_arrival": "2023-04-07T16:00:00.000Z", "local_departure": "2023-04-07T14:50:00.000Z", "utc_departure": "2023-04-07T12:50:00.000Z"}], "booking_token": "EIa_jS2zmfMg0CRvlfmh5FMjW11RuaVChERsFsP2tIDHCj9jnv2q6BcNg9ssjHd6qjPlktGFsc-Fr9S6JWPEKJ3RusOjlito7jpe1PbgdULKX8KKen3Lq0nnE9lK9GyzQS1DCLyor6zVO35Rgmbn_XnMDFk2x3xRW1SWESc_29dlPFz7MZxvEO9IUGBwetXGxlnKDa8M0Dcyx7QGIMKya4lw74-XwwWrfGbvDX1yfQ3FIUufMXvKE0RDo7LkHPkDTjODozWzC1bIlJcpnudKKuw6dComsPBzk10l3DrvHJGtO7_q3AtvD9A-Zs0T26_VUNBETGEbgID-ZQgThjUqzYfm7BViWAlL53sMIcynS7gvxiTbAFuGXEGGLDpsktjQgyfnRSoXLzW5bdN0UDW5x7xgZCWpMRGdzd4WK64r1_mMinkTaqQJYEmoP1NTyP2Z49eF40gZy03zN636h6ciJJIcDoHYBSP-aoruEnd3X5A5A472ywC42hkS0CYOExJ6u1_f32Oskuq0ZcQ8f8aEImPxfPNVymigTnzQfF-EhfOuH4P5Vzh-g0eEWtLqalHNSdnp8LY8GF3D8whJUC2tzuwgsiov_PUjszmgChYx1B3VOjVgr8eKvkjdDxunIX1g0qZl6m_tpGIKpTi1XFf242bQyx8em-Mi7Jwvmzv3H0MjT3uhM8zVlUok10dk2Nr92ZY4m06BxgAf1nNAGf6KrHskM7v70h06FI5E6hEaka7QujsSee2edA2_0rwuCIp1CKS7Sro-0wtwE4c_3Q_5LCw==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224bfb0000cba453bb_0%7C0a220b774bfe000002ec78b7_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EIa_jS2zmfMg0CRvlfmh5FMjW11RuaVChERsFsP2tIDHCj9jnv2q6BcNg9ssjHd6qjPlktGFsc-Fr9S6JWPEKJ3RusOjlito7jpe1PbgdULKX8KKen3Lq0nnE9lK9GyzQS1DCLyor6zVO35Rgmbn_XnMDFk2x3xRW1SWESc_29dlPFz7MZxvEO9IUGBwetXGxlnKDa8M0Dcyx7QGIMKya4lw74-XwwWrfGbvDX1yfQ3FIUufMXvKE0RDo7LkHPkDTjODozWzC1bIlJcpnudKKuw6dComsPBzk10l3DrvHJGtO7_q3AtvD9A-Zs0T26_VUNBETGEbgID-ZQgThjUqzYfm7BViWAlL53sMIcynS7gvxiTbAFuGXEGGLDpsktjQgyfnRSoXLzW5bdN0UDW5x7xgZCWpMRGdzd4WK64r1_mMinkTaqQJYEmoP1NTyP2Z49eF40gZy03zN636h6ciJJIcDoHYBSP-aoruEnd3X5A5A472ywC42hkS0CYOExJ6u1_f32Oskuq0ZcQ8f8aEImPxfPNVymigTnzQfF-EhfOuH4P5Vzh-g0eEWtLqalHNSdnp8LY8GF3D8whJUC2tzuwgsiov_PUjszmgChYx1B3VOjVgr8eKvkjdDxunIX1g0qZl6m_tpGIKpTi1XFf242bQyx8em-Mi7Jwvmzv3H0MjT3uhM8zVlUok10dk2Nr92ZY4m06BxgAf1nNAGf6KrHskM7v70h06FI5E6hEaka7QujsSee2edA2_0rwuCIp1CKS7Sro-0wtwE4c_3Q_5LCw==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-04-04T10:15:00.000Z", "utc_arrival": "2023-04-04T08:15:00.000Z", "local_departure": "2023-04-04T06:55:00.000Z", "utc_departure": "2023-04-04T04:55:00.000Z"}, {"id": "0b770a224c1a0000fc0feb0f_0|0a220b774c1d000091abd9a6_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 784.787398, "distance": 1975.87, "duration": {"departure": 12600, "return": 11700, "total": 24300}, "price": 240201.0341, "conversion": {"EUR": 628.787788, "HUF": 240201.0341}, "fare": {"adults": 120100.52, "children": 123157.6, "infants": 123157.6}, "bags_price": {"1": 89.768, "2": 179.536}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 439, "hold_height": 149, "hold_length": 171, "hold_weight": 20, "hold_width": 119, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 6}, "airlines": ["W6"], "route": [{"id": "0b770a224c1a0000fc0feb0f_0", "combination_id": "0b770a224c1a0000fc0feb0f", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "JREG", "fare_category": "M", "fare_classes": "J", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-05T19:45:00.000Z", "utc_arrival": "2023-05-05T17:45:00.000Z", "local_departure": "2023-05-05T16:15:00.000Z", "utc_departure": "2023-05-05T14:15:00.000Z"}, {"id": "0a220b774c1d000091abd9a6_0", "combination_id": "0a220b774c1d000091abd9a6", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "GREG", "fare_category": "M", "fare_classes": "G", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-08T23:45:00.000Z", "utc_arrival": "2023-05-08T21:45:00.000Z", "local_departure": "2023-05-08T20:30:00.000Z", "utc_departure": "2023-05-08T18:30:00.000Z"}], "booking_token": "ExsxnKjoCqF0ECXkmxRxMbP4nWA7WTF75-dWpo3UPP8QDn7MDFGEJ26TmLkUeJqezXYkfypKsPF6Bhq41sXwPYOXn0ignFkhahnTOsFCtt3nhW_WLt3pQTFC80lYF-VEW8jSHTGGjvJ4cHwwEJjGi7NaVarIhVqn01enxqEn7zyu5rsAOkQ4hi2_wfBOqOgAN_Dd8_2mrlNCKKZrvM2iGky_AiH9-KnMZv154j_UAUxRLpfFKvp4PHL7p3d9KEoCN2Qb7elVA7ZUl1H0v8yzNv6Zv2MsnoBLLgUvAI7TTguda6U1T_ZYJMpLk4Um3Sp_mG6Al9Ruoc-J8lSuZu1_61cAJ1OrOcmUxOB-UHdAS86_lZsimVp4MvfyHV34mOIKeH3xRML-6ETTSJlkUXUJtvx_ecO6qHp56anSpf1-iu-hQ76YxOi1GeQrYI7KXGdjYE1XBpqedy0zWJlKX4XvNQ4IXkU0744y1DFfPEhxGWp6BM-uXVR5KoeGc4Jq084gt0SPsPr98ZcCbemr7Lzh4qYueiV4QgXq3B4RytQLgYCTEdB7N8fkyeZIDs_B7mrlyWeXSeM3Y9oTDpVozpVgwQnnb_hn2P6bMQI54Cy292WcrhLO7kxWbkOuGerrVew5Ph7ENPRhUAxvukx-rxa2x6tnIflRxbo7NRHWIUIs1U9PjhE7dmlpKinxgFBRx9WSZwmiAz_SIQa8Be3RvQCU_l0OWfWIxTpdLoPcwS8gkt2hdvrepU1Mag5TFJgIy7VzPfQSIW9dE45A6VmMdDx7p5CjaizMeTixoVxQLyg_gJGQ=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c1a0000fc0feb0f_0%7C0a220b774c1d000091abd9a6_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=ExsxnKjoCqF0ECXkmxRxMbP4nWA7WTF75-dWpo3UPP8QDn7MDFGEJ26TmLkUeJqezXYkfypKsPF6Bhq41sXwPYOXn0ignFkhahnTOsFCtt3nhW_WLt3pQTFC80lYF-VEW8jSHTGGjvJ4cHwwEJjGi7NaVarIhVqn01enxqEn7zyu5rsAOkQ4hi2_wfBOqOgAN_Dd8_2mrlNCKKZrvM2iGky_AiH9-KnMZv154j_UAUxRLpfFKvp4PHL7p3d9KEoCN2Qb7elVA7ZUl1H0v8yzNv6Zv2MsnoBLLgUvAI7TTguda6U1T_ZYJMpLk4Um3Sp_mG6Al9Ruoc-J8lSuZu1_61cAJ1OrOcmUxOB-UHdAS86_lZsimVp4MvfyHV34mOIKeH3xRML-6ETTSJlkUXUJtvx_ecO6qHp56anSpf1-iu-hQ76YxOi1GeQrYI7KXGdjYE1XBpqedy0zWJlKX4XvNQ4IXkU0744y1DFfPEhxGWp6BM-uXVR5KoeGc4Jq084gt0SPsPr98ZcCbemr7Lzh4qYueiV4QgXq3B4RytQLgYCTEdB7N8fkyeZIDs_B7mrlyWeXSeM3Y9oTDpVozpVgwQnnb_hn2P6bMQI54Cy292WcrhLO7kxWbkOuGerrVew5Ph7ENPRhUAxvukx-rxa2x6tnIflRxbo7NRHWIUIs1U9PjhE7dmlpKinxgFBRx9WSZwmiAz_SIQa8Be3RvQCU_l0OWfWIxTpdLoPcwS8gkt2hdvrepU1Mag5TFJgIy7VzPfQSIW9dE45A6VmMdDx7p5CjaizMeTixoVxQLyg_gJGQ=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-05T19:45:00.000Z", "utc_arrival": "2023-05-05T17:45:00.000Z", "local_departure": "2023-05-05T16:15:00.000Z", "utc_departure": "2023-05-05T14:15:00.000Z"}, {"id": "0b770a224c390000c8acc8ed_0|0a220b774c3c00005d56eab0_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 785.185512, "distance": 1975.87, "duration": {"departure": 12600, "return": 11700, "total": 24300}, "price": 240353.1162, "conversion": {"EUR": 629.185902, "HUF": 240353.1162}, "fare": {"adults": 120176.56, "children": 126499.34, "infants": 126499.34}, "bags_price": {"1": 111.524, "2": 223.048}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 439, "hold_height": 149, "hold_length": 171, "hold_weight": 20, "hold_width": 119, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 7}, "airlines": ["W6"], "route": [{"id": "0b770a224c390000c8acc8ed_0", "combination_id": "0b770a224c390000c8acc8ed", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "HREG", "fare_category": "M", "fare_classes": "H", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-05T19:45:00.000Z", "utc_arrival": "2023-06-05T17:45:00.000Z", "local_departure": "2023-06-05T16:15:00.000Z", "utc_departure": "2023-06-05T14:15:00.000Z"}, {"id": "0a220b774c3c00005d56eab0_0", "combination_id": "0a220b774c3c00005d56eab0", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-09T01:15:00.000Z", "utc_arrival": "2023-06-08T23:15:00.000Z", "local_departure": "2023-06-08T22:00:00.000Z", "utc_departure": "2023-06-08T20:00:00.000Z"}], "booking_token": "EB6hFBAJBW0yybPFI4nSpzu5M8Uy_h0VF9voX9D8HsCf6IcxIYvf5eubU7PyhdbjE2ibcoLFbKqVoao3D470nNxETd_a7IrlupURGq2Rap3qLZw5VFhWjuq5RN5dXfcgRzZH9XXx0ERk8WwartcMkwOimpEySols0BS59gw3T9e9269i0xAkegm-ouQ1Xi4HLHi-COvPJSUf7s_7obIXPVimj-eVFQZjLt9ZwqwEYNlzdvkymclND9lzKa_OHIiiA3qE6qqMv8XSitNH124YGTSa-XXsVQZY1WY0Et0Byu1RDcdqTbto-MGfEW-EhXoq3QU6rlKwim3KruICAqbs_AjDTf1nNRkLLP5nLyR6bEP-GursAVXc3tAgNxoEv33aRSIjV8Tkdu_f3LVq5sTIg92X8UTQKRi75IzG5oGYtPnrirXe-trJ4UKU228e-1TESu-tsUfwoHNTTgixGM_54DekDwIXFQZ9_xEuazLZm6jUTncdidyHGLOhl3AYmrtozTdx77MbiIw4x4rBvibSunZUShTMkmb3sD4nxeGYxgP4-n9GvMkYfzal9neXSHOD8Sh2Z6xepdUS1ClWDKN7wIs28tvlzU4CLsj75OEQJc160U92gps3CiKp2BO-nyKKfDFjH8O_GN8NxMsiE4P_hP16zffXkptaI0975667Io97xG9Xyaqg6f8KL_fMZVCB-7PNEGZolDH6SwR58ICGMjRpIlL6XpIiMS_zzMmkt1NdgTNHv5mVUSnGmZ2-toNd8DbLYRuNJlmyZcGKR7frLMxIbfGKQNbDP8iwT6YDFpPU=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c390000c8acc8ed_0%7C0a220b774c3c00005d56eab0_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EB6hFBAJBW0yybPFI4nSpzu5M8Uy_h0VF9voX9D8HsCf6IcxIYvf5eubU7PyhdbjE2ibcoLFbKqVoao3D470nNxETd_a7IrlupURGq2Rap3qLZw5VFhWjuq5RN5dXfcgRzZH9XXx0ERk8WwartcMkwOimpEySols0BS59gw3T9e9269i0xAkegm-ouQ1Xi4HLHi-COvPJSUf7s_7obIXPVimj-eVFQZjLt9ZwqwEYNlzdvkymclND9lzKa_OHIiiA3qE6qqMv8XSitNH124YGTSa-XXsVQZY1WY0Et0Byu1RDcdqTbto-MGfEW-EhXoq3QU6rlKwim3KruICAqbs_AjDTf1nNRkLLP5nLyR6bEP-GursAVXc3tAgNxoEv33aRSIjV8Tkdu_f3LVq5sTIg92X8UTQKRi75IzG5oGYtPnrirXe-trJ4UKU228e-1TESu-tsUfwoHNTTgixGM_54DekDwIXFQZ9_xEuazLZm6jUTncdidyHGLOhl3AYmrtozTdx77MbiIw4x4rBvibSunZUShTMkmb3sD4nxeGYxgP4-n9GvMkYfzal9neXSHOD8Sh2Z6xepdUS1ClWDKN7wIs28tvlzU4CLsj75OEQJc160U92gps3CiKp2BO-nyKKfDFjH8O_GN8NxMsiE4P_hP16zffXkptaI0975667Io97xG9Xyaqg6f8KL_fMZVCB-7PNEGZolDH6SwR58ICGMjRpIlL6XpIiMS_zzMmkt1NdgTNHv5mVUSnGmZ2-toNd8DbLYRuNJlmyZcGKR7frLMxIbfGKQNbDP8iwT6YDFpPU=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-05T19:45:00.000Z", "utc_arrival": "2023-06-05T17:45:00.000Z", "local_departure": "2023-06-05T16:15:00.000Z", "utc_departure": "2023-06-05T14:15:00.000Z"}, {"id": "0b770a224c290000e8e2d43c_0|0a220b774c2c0000c29499a5_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 781.929135, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 240637.1812, "conversion": {"EUR": 629.929515, "HUF": 240637.1812}, "fare": {"adults": 120318.59, "children": 127529.05, "infants": 127529.05}, "bags_price": {"1": 75.768, "2": 161.322}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 158, "hold_height": 52, "hold_length": 78, "hold_weight": 20, "hold_width": 28, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 3, "personal_item_width": 15}, "availability": {"seats": 3}, "airlines": ["FR", "IB"], "route": [{"id": "0b770a224c290000e8e2d43c_0", "combination_id": "0b770a224c290000e8e2d43c", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-20T13:25:00.000Z", "utc_arrival": "2023-05-20T11:25:00.000Z", "local_departure": "2023-05-20T10:05:00.000Z", "utc_departure": "2023-05-20T08:05:00.000Z"}, {"id": "0a220b774c2c0000c29499a5_0", "combination_id": "0a220b774c2c0000c29499a5", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "IB", "flight_no": 3278, "operating_carrier": "IB", "operating_flight_no": "3278", "fare_basis": "VDNNAOB4", "fare_category": "M", "fare_classes": "V", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-23T14:55:00.000Z", "utc_arrival": "2023-05-23T12:55:00.000Z", "local_departure": "2023-05-23T11:45:00.000Z", "utc_departure": "2023-05-23T09:45:00.000Z"}], "booking_token": "EGzAmHkvwfQdxelpVMVA56Lt-hvuJiigwxVjE1QAvSz63TY7uhv0B5LpVKX6sSyp4eMlhYxtOA3LXpusO4cOoYAe3J4TinVi0zY6EFoJZxCkGkrvUomjtHhM_gBzAUWbcSCmePGwa0gPQILquH6I_dh8o3eSAaQ2MlF2TRvPmt0Y2atfexwsgMlk264lYdY4niKbQbdG7p7KSi6CLx5_D-v8qZ0DQAC5hTlZv2fv7gJPOh9Ay9igObfCVJniWPXcDqBZrUSEIskYcPQP5HnnjRcMKV1Yu8UlTqblwwEo7i1hI49EwK4Ol6kKMdcIzAgxnW-lP46RRGHr-W0FzE07p9SvBAYJPfHUxf9kwxxge0-CXMLXHH6_Q3vGLCs7Az07wHOHmRtPpv2Uj6T3W2TjFrb3iWu7FLnOL9GcskAUBbv-jMGsIOKSDKFkHMSamkGG8XJkurUBpzDg_NEWu03WmY7N49IFO1WutMVWMdrL6pGQuNx5ngTM07SxAx5qjBfa_aGCXugRiZ5dGtbhUtgciLDAMCijH-4hsVVpBPBdJCU7UtpG6YpqnD4tQR_t99LRVUcv4s8-r8q0tnQTzn1T0eID1rHXNd8OfG3_8Rai6HzmTphzCygK7RKWRF_Wk58CgOD-a0oTyxZfwn_YUSRQNz9c3Yqermi4t92hoRElll1ZzbYMClgP7rGWhBKtur7wLjQ0zr3iBUK7vpGGvkYG4rW1bjWie4q1Ydb_WaGzS2W9OoYbvKNZSDlp3N5KHytkOMcj3ThP1pT65sbkVTYukJ80cExnGCe6fA7KmPDrt9Sk=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c290000e8e2d43c_0%7C0a220b774c2c0000c29499a5_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EGzAmHkvwfQdxelpVMVA56Lt-hvuJiigwxVjE1QAvSz63TY7uhv0B5LpVKX6sSyp4eMlhYxtOA3LXpusO4cOoYAe3J4TinVi0zY6EFoJZxCkGkrvUomjtHhM_gBzAUWbcSCmePGwa0gPQILquH6I_dh8o3eSAaQ2MlF2TRvPmt0Y2atfexwsgMlk264lYdY4niKbQbdG7p7KSi6CLx5_D-v8qZ0DQAC5hTlZv2fv7gJPOh9Ay9igObfCVJniWPXcDqBZrUSEIskYcPQP5HnnjRcMKV1Yu8UlTqblwwEo7i1hI49EwK4Ol6kKMdcIzAgxnW-lP46RRGHr-W0FzE07p9SvBAYJPfHUxf9kwxxge0-CXMLXHH6_Q3vGLCs7Az07wHOHmRtPpv2Uj6T3W2TjFrb3iWu7FLnOL9GcskAUBbv-jMGsIOKSDKFkHMSamkGG8XJkurUBpzDg_NEWu03WmY7N49IFO1WutMVWMdrL6pGQuNx5ngTM07SxAx5qjBfa_aGCXugRiZ5dGtbhUtgciLDAMCijH-4hsVVpBPBdJCU7UtpG6YpqnD4tQR_t99LRVUcv4s8-r8q0tnQTzn1T0eID1rHXNd8OfG3_8Rai6HzmTphzCygK7RKWRF_Wk58CgOD-a0oTyxZfwn_YUSRQNz9c3Yqermi4t92hoRElll1ZzbYMClgP7rGWhBKtur7wLjQ0zr3iBUK7vpGGvkYG4rW1bjWie4q1Ydb_WaGzS2W9OoYbvKNZSDlp3N5KHytkOMcj3ThP1pT65sbkVTYukJ80cExnGCe6fA7KmPDrt9Sk=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-20T13:25:00.000Z", "utc_arrival": "2023-05-20T11:25:00.000Z", "local_departure": "2023-05-20T10:05:00.000Z", "utc_departure": "2023-05-20T08:05:00.000Z"}, {"id": "0b770a224c2e0000339b474d_0|0a220b774c320000e133d3ca_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 784.775744, "distance": 1975.87, "duration": {"departure": 12600, "return": 11400, "total": 24000}, "price": 240705.9229, "conversion": {"EUR": 630.109464, "HUF": 240705.9229}, "fare": {"adults": 120352.96, "children": 123450.28, "infants": 123450.28}, "bags_price": {"1": 66.626, "2": 133.238}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 3}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224c2e0000339b474d_0", "combination_id": "0b770a224c2e0000339b474d", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "HREG", "fare_category": "M", "fare_classes": "H", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-25T21:15:00.000Z", "utc_arrival": "2023-05-25T19:15:00.000Z", "local_departure": "2023-05-25T17:45:00.000Z", "utc_departure": "2023-05-25T15:45:00.000Z"}, {"id": "0a220b774c320000e133d3ca_0", "combination_id": "0a220b774c320000e133d3ca", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-29T10:15:00.000Z", "utc_arrival": "2023-05-29T08:15:00.000Z", "local_departure": "2023-05-29T07:05:00.000Z", "utc_departure": "2023-05-29T05:05:00.000Z"}], "booking_token": "EGyvlVu3NsRJAZVtircwe0dXv-c6mD6lGXB_ikNDjAItDANX8S8tJ818c6nBhgNtOFLVz5C8MwN3iooUV5zuQBPNEetoAci7zIP2KffmxKoOhu9wa4X2efdAslH7gz6nlJOQA7_FFJkNlr94jEMZ3CZOJRKxUhbmaRWikrDJEsQU9usqvtX-FtyA5pdlXJuK8kPJKmBfAZsAAAq1StkS3yXW5FYfdviiIL2C7uX7ioAWtMTh8KGmuqqZos95ETxfKCjhFvxX6cjbAwwJPW7Ya-780xgh-BoQOD-ZOmlsj5hBGJqcSr2bKXZVLk5AT_haImHPcFk77gugXrKOuvsbDKN80P-m7pL_cepfLRP06eRtTv-kuypDJAbr2HrGe6gJ5mQ0FIJt3wOv0jjmcVW5Jd2D0IVImy-O52FryNehWuYTrRnjBv2d8A1rqDV6-ZlqzBBpOYRjNWZWKBvvZTEoBX5sWbuDT6RSSZ5ybfn7bL5CrGOpIOjb6EDbdY4vXnkI_h3qHQkyvOuFblG7mqp7vUNB8A4OJJOBNvRsOrSxvAoew-NW0Axwt7UEfTUpFlRb7v5Co2H53B3YuknuGFe8gyEO7baCGrCthI02cZzXk4TUWSyCvt9QcbIIDB6A0E8KuE5hX0yGxGq5qrdCDHkeR2g48KSG4iWvcFnQch4e9Ol4GM2dIYzW38mB5AZZFeh0Z8ZDDAucxiqXGfh2mbKfWLPZQhulUj5R4RZQbq8S6xvx3UtTyHa3KkohXoVztQEpa1HruzfzipKaFhd7HQrTlZw==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c2e0000339b474d_0%7C0a220b774c320000e133d3ca_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EGyvlVu3NsRJAZVtircwe0dXv-c6mD6lGXB_ikNDjAItDANX8S8tJ818c6nBhgNtOFLVz5C8MwN3iooUV5zuQBPNEetoAci7zIP2KffmxKoOhu9wa4X2efdAslH7gz6nlJOQA7_FFJkNlr94jEMZ3CZOJRKxUhbmaRWikrDJEsQU9usqvtX-FtyA5pdlXJuK8kPJKmBfAZsAAAq1StkS3yXW5FYfdviiIL2C7uX7ioAWtMTh8KGmuqqZos95ETxfKCjhFvxX6cjbAwwJPW7Ya-780xgh-BoQOD-ZOmlsj5hBGJqcSr2bKXZVLk5AT_haImHPcFk77gugXrKOuvsbDKN80P-m7pL_cepfLRP06eRtTv-kuypDJAbr2HrGe6gJ5mQ0FIJt3wOv0jjmcVW5Jd2D0IVImy-O52FryNehWuYTrRnjBv2d8A1rqDV6-ZlqzBBpOYRjNWZWKBvvZTEoBX5sWbuDT6RSSZ5ybfn7bL5CrGOpIOjb6EDbdY4vXnkI_h3qHQkyvOuFblG7mqp7vUNB8A4OJJOBNvRsOrSxvAoew-NW0Axwt7UEfTUpFlRb7v5Co2H53B3YuknuGFe8gyEO7baCGrCthI02cZzXk4TUWSyCvt9QcbIIDB6A0E8KuE5hX0yGxGq5qrdCDHkeR2g48KSG4iWvcFnQch4e9Ol4GM2dIYzW38mB5AZZFeh0Z8ZDDAucxiqXGfh2mbKfWLPZQhulUj5R4RZQbq8S6xvx3UtTyHa3KkohXoVztQEpa1HruzfzipKaFhd7HQrTlZw==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-25T21:15:00.000Z", "utc_arrival": "2023-05-25T19:15:00.000Z", "local_departure": "2023-05-25T17:45:00.000Z", "utc_departure": "2023-05-25T15:45:00.000Z"}, {"id": "0b770a224c0b000076bbcc9c_0|0a220b774c0f0000a1c65665_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 781.123416, "distance": 1975.87, "duration": {"departure": 11700, "return": 11400, "total": 23100}, "price": 240838.7321, "conversion": {"EUR": 630.457126, "HUF": 240838.7321}, "fare": {"adults": 120419.37, "children": 120419.37, "infants": 120419.37}, "bags_price": {"1": 85.386, "2": 180.572}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 158, "hold_height": 52, "hold_length": 78, "hold_weight": 20, "hold_width": 28, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 3, "personal_item_width": 15}, "availability": {"seats": 5}, "airlines": ["FR", "IB"], "route": [{"id": "0b770a224c0b000076bbcc9c_0", "combination_id": "0b770a224c0b000076bbcc9c", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "IB", "flight_no": 3279, "operating_carrier": "IB", "operating_flight_no": "3279", "fare_basis": "QDNNAOB4", "fare_category": "M", "fare_classes": "Q", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-20T18:50:00.000Z", "utc_arrival": "2023-04-20T16:50:00.000Z", "local_departure": "2023-04-20T15:35:00.000Z", "utc_departure": "2023-04-20T13:35:00.000Z"}, {"id": "0a220b774c0f0000a1c65665_0", "combination_id": "0a220b774c0f0000a1c65665", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-24T10:15:00.000Z", "utc_arrival": "2023-04-24T08:15:00.000Z", "local_departure": "2023-04-24T07:05:00.000Z", "utc_departure": "2023-04-24T05:05:00.000Z"}], "booking_token": "ELKUXeVd7fLm1bhOen_AP2KX1xAQ-2CvzAwA5NW1sCkH6QuquWsL-VZEdTBAzhTz7AcxAtSKj2YI0Cgtil5cVDpGgTjHxn41dJx3mqjVd7as4KSh5q8Z_NfBnZH0HXbJm326j0L74lj-NXNdtOJBbrJFh-srxjhoJspMdi1yccw1qiDhhdvjrZU7O-0YlGO-yBw3dyKeJ1Yw9Oii5vz-B-OEKa4uPAe8x35kSWlcIkAC8FZCAk_CFCn0u9TkZq7lzDHfz9QrYWJTWtu2iILbdDXtpXP6Zdb6rK4mBl_SHkZnb79eRbmixrVVbvCBucazdaxYIkLkEVi7qRM5zyfs7Zu_U1PHHZaVQllgo0UM3lj_cjLZ73u_89rlZ9w1iz23baBYYLFdG-HjzL2RSyrsFwLNTNnY10oMCDOQb0xYeiR7kvvj8fLNAtdBI9ClO1yQF3hq3P2Rfxn_v_99vrjN3Z-E18l6P0D3y8DJDPtMyG3DPmBkDtBCyxNMJozFMNj_-BtSRZXsxpSxtLpIhYMeSyrGDIIQQNPit7i40mQ4YVNIKxRyM4nHkHeUKbPzopRD2Ij7KVhDJ08P2lBNr4xSzq0KCsxXDdkssUqFpSFrxz149XBFPNA_0Y89-BsiN4O3v87A6Y1NqIinRCq9mViz0iBFYTaWrw3G8FImCHodf4t7g4ZK2SmQqA5HHCGQHzBRXhwgL19sqcR0OR57BGkBfvbAlLYAKGkz1e8Y3E8GAJDudkvy6vtSh0lSc_2XTzmhBDRAjdQ9vNSIx2zD4g2tDO0xto5dq4vo-5dsTw75NTnY=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c0b000076bbcc9c_0%7C0a220b774c0f0000a1c65665_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=ELKUXeVd7fLm1bhOen_AP2KX1xAQ-2CvzAwA5NW1sCkH6QuquWsL-VZEdTBAzhTz7AcxAtSKj2YI0Cgtil5cVDpGgTjHxn41dJx3mqjVd7as4KSh5q8Z_NfBnZH0HXbJm326j0L74lj-NXNdtOJBbrJFh-srxjhoJspMdi1yccw1qiDhhdvjrZU7O-0YlGO-yBw3dyKeJ1Yw9Oii5vz-B-OEKa4uPAe8x35kSWlcIkAC8FZCAk_CFCn0u9TkZq7lzDHfz9QrYWJTWtu2iILbdDXtpXP6Zdb6rK4mBl_SHkZnb79eRbmixrVVbvCBucazdaxYIkLkEVi7qRM5zyfs7Zu_U1PHHZaVQllgo0UM3lj_cjLZ73u_89rlZ9w1iz23baBYYLFdG-HjzL2RSyrsFwLNTNnY10oMCDOQb0xYeiR7kvvj8fLNAtdBI9ClO1yQF3hq3P2Rfxn_v_99vrjN3Z-E18l6P0D3y8DJDPtMyG3DPmBkDtBCyxNMJozFMNj_-BtSRZXsxpSxtLpIhYMeSyrGDIIQQNPit7i40mQ4YVNIKxRyM4nHkHeUKbPzopRD2Ij7KVhDJ08P2lBNr4xSzq0KCsxXDdkssUqFpSFrxz149XBFPNA_0Y89-BsiN4O3v87A6Y1NqIinRCq9mViz0iBFYTaWrw3G8FImCHodf4t7g4ZK2SmQqA5HHCGQHzBRXhwgL19sqcR0OR57BGkBfvbAlLYAKGkz1e8Y3E8GAJDudkvy6vtSh0lSc_2XTzmhBDRAjdQ9vNSIx2zD4g2tDO0xto5dq4vo-5dsTw75NTnY=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-04-20T18:50:00.000Z", "utc_arrival": "2023-04-20T16:50:00.000Z", "local_departure": "2023-04-20T15:35:00.000Z", "utc_departure": "2023-04-20T13:35:00.000Z"}, {"id": "0b770a224c040000025fb1e5_0|0a220b774c0800003a297c03_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 785.69518, "distance": 1975.87, "duration": {"departure": 12600, "return": 11400, "total": 24000}, "price": 241057.1535, "conversion": {"EUR": 631.0289, "HUF": 241057.1535}, "fare": {"adults": 120528.58, "children": 120528.58, "infants": 120528.58}, "bags_price": {"1": 99.61, "2": 199.206}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 3}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224c040000025fb1e5_0", "combination_id": "0b770a224c040000025fb1e5", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-13T21:15:00.000Z", "utc_arrival": "2023-04-13T19:15:00.000Z", "local_departure": "2023-04-13T17:45:00.000Z", "utc_departure": "2023-04-13T15:45:00.000Z"}, {"id": "0a220b774c0800003a297c03_0", "combination_id": "0a220b774c0800003a297c03", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-17T10:15:00.000Z", "utc_arrival": "2023-04-17T08:15:00.000Z", "local_departure": "2023-04-17T07:05:00.000Z", "utc_departure": "2023-04-17T05:05:00.000Z"}], "booking_token": "EtZ6L6uuE2GC-pc3Li1hY0v_d4lDg0gHIsftrBy1RlQaxJld9dABGmeH2bClpsZ97WFnZitx5z_UxewCCznYLAjMcFMD9yjmP_2qo4PFnk0n-XNgExIdX8fHKkjj9idnskYrIn9O_ropTA3zg7Pm77UjsgCGLXm97dsi89PpJeFS1BBOLmE-2fHBjjZojhJWWZzLgPERqwHuD0xC845GhXNIqQed6Om-pFwunaRBkp86hwjgVsz3lXbuV7dNumPDHI2QlSHmQ-nH_nqtIRj9lKytf2bBCb9XfHxBssU267Ahr6FiKJIXRQbdKf0E5omlaVPnA06hiC8jUmDbtr5PhcVyeUu9Ko6JPNCSHEIC9pp8W5a6dTUJUqMgaKPXB-urKliMRwIXmTGkRkHJzLPAGe2nbiRTjOhDqcP6spm-KtqtUeV4WunewwEUX7_yk_mVnUL4EyhjmkjAInAwv5M_8rveE6eCyy-b1Tq2gGK5-R2S6Me0zA1JdB9hEAAqyJzdrI-bkpSQxqLIblcE_bx0J9r55mLqJcsP8d2-itZ29G9N-QYGOhQjC49VpUe9pDZNZKqG0ftGmWuC1gimqYJPJE2_QCjSv7q9a1d6ODzpSVFoBEY7Fq5idRmJAH1kjudAkkGr_bcjWARzSW4isk11V2y1GLLhgbCcr5qi9LglGerDRDi4QhYblWLa1uIb_lS67iPDEqbtHeKPRxU6Zw0mRkzGLzQPP9m2nCruSMLDWreRxdlq_p18mD27uDD8hiCYaQCRfjkl2gSPqWXUEYL-KZiQNVy-24llHIYFzMqp-efA=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c040000025fb1e5_0%7C0a220b774c0800003a297c03_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EtZ6L6uuE2GC-pc3Li1hY0v_d4lDg0gHIsftrBy1RlQaxJld9dABGmeH2bClpsZ97WFnZitx5z_UxewCCznYLAjMcFMD9yjmP_2qo4PFnk0n-XNgExIdX8fHKkjj9idnskYrIn9O_ropTA3zg7Pm77UjsgCGLXm97dsi89PpJeFS1BBOLmE-2fHBjjZojhJWWZzLgPERqwHuD0xC845GhXNIqQed6Om-pFwunaRBkp86hwjgVsz3lXbuV7dNumPDHI2QlSHmQ-nH_nqtIRj9lKytf2bBCb9XfHxBssU267Ahr6FiKJIXRQbdKf0E5omlaVPnA06hiC8jUmDbtr5PhcVyeUu9Ko6JPNCSHEIC9pp8W5a6dTUJUqMgaKPXB-urKliMRwIXmTGkRkHJzLPAGe2nbiRTjOhDqcP6spm-KtqtUeV4WunewwEUX7_yk_mVnUL4EyhjmkjAInAwv5M_8rveE6eCyy-b1Tq2gGK5-R2S6Me0zA1JdB9hEAAqyJzdrI-bkpSQxqLIblcE_bx0J9r55mLqJcsP8d2-itZ29G9N-QYGOhQjC49VpUe9pDZNZKqG0ftGmWuC1gimqYJPJE2_QCjSv7q9a1d6ODzpSVFoBEY7Fq5idRmJAH1kjudAkkGr_bcjWARzSW4isk11V2y1GLLhgbCcr5qi9LglGerDRDi4QhYblWLa1uIb_lS67iPDEqbtHeKPRxU6Zw0mRkzGLzQPP9m2nCruSMLDWreRxdlq_p18mD27uDD8hiCYaQCRfjkl2gSPqWXUEYL-KZiQNVy-24llHIYFzMqp-efA=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-04-13T21:15:00.000Z", "utc_arrival": "2023-04-13T19:15:00.000Z", "local_departure": "2023-04-13T17:45:00.000Z", "utc_departure": "2023-04-13T15:45:00.000Z"}, {"id": "0b770a224c350000fd39ce98_0|0a220b774c390000563d5408_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 787.144533, "distance": 1975.87, "duration": {"departure": 12600, "return": 11700, "total": 24300}, "price": 241101.475, "conversion": {"EUR": 631.144923, "HUF": 241101.475}, "fare": {"adults": 120550.74, "children": 123606.21, "infants": 123606.21}, "bags_price": {"1": 117.348, "2": 234.696}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 439, "hold_height": 149, "hold_length": 171, "hold_weight": 20, "hold_width": 119, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 5}, "airlines": ["W6"], "route": [{"id": "0b770a224c350000fd39ce98_0", "combination_id": "0b770a224c350000fd39ce98", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "HREG", "fare_category": "M", "fare_classes": "H", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-01T21:15:00.000Z", "utc_arrival": "2023-06-01T19:15:00.000Z", "local_departure": "2023-06-01T17:45:00.000Z", "utc_departure": "2023-06-01T15:45:00.000Z"}, {"id": "0a220b774c390000563d5408_0", "combination_id": "0a220b774c390000563d5408", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-05T23:45:00.000Z", "utc_arrival": "2023-06-05T21:45:00.000Z", "local_departure": "2023-06-05T20:30:00.000Z", "utc_departure": "2023-06-05T18:30:00.000Z"}], "booking_token": "E-6FDClyGaXfsWiHs7DqTt1Z1nvIN2AXCjZAdm-jEpy6RH6R-XAhrr2qiPATeigkJbJoylh4D3rV4fodqXx30PMOGMWNq0Kn7MKzah9RER-TlbicYX_5G1X5EtI8c1SszQuP3YEHoJdVmFt-poXF8bj0JMS935-l4eoBuLZw2qNgI0bARyJvJ6cbH-9FM8vFrJALG47muTvtU43NKRe9-OHMa94_-GA1MZL2x_un9j-zEO-Xk9SHOiE41Wr1cuCC8Cu4tiX0sZWCxHoRjRtBFwSKaFKREvuWfnwC3Y31z9eSr0useQinwLUNoZitzDFI8x7e57acDpk-9c6ZznRnwyl-MwRNdJFH2MNh6nee1a77pHkjVyKc__Jm7KMzI95KM8mQuFd11W65KlF_rKdnjhDARUCiYfuSQqLvruFaoVePXsMqWQ29P33w-r3GeaAR_cLRCzeRa8BPeLkmm_cKDX-x11b_jSsx4Sz-9r7pnjLZBAeQ3hIiUAAHppfCJtKsjX_huhzQk3ErAwpIA196gREUC03p2Qb0zZJlq3WswissRVYVwc2fBPrPgH8HWrSexXFmkbJTZPWawIuDd32NBIWJyAHfY0ZyqXFFxA_uXw--2-IAvwDALCf454Yuq3mCnQesg55VPTAC6HWru6UftvyMEf7b1WXwnx6eVoqU9APxNPbGmc07hZpEZR4Gh2zplNY5i47AEIlSlWJw6yw-Je_wJ8APPaxfPj5J3UjGIDHCZ2Wwcd7JRncEZ1v4TYJU1ngOsTjJnBpVHwUZ8EeLOiZwZ-mDleg9J6pZjlkcfSdg=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c350000fd39ce98_0%7C0a220b774c390000563d5408_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=E-6FDClyGaXfsWiHs7DqTt1Z1nvIN2AXCjZAdm-jEpy6RH6R-XAhrr2qiPATeigkJbJoylh4D3rV4fodqXx30PMOGMWNq0Kn7MKzah9RER-TlbicYX_5G1X5EtI8c1SszQuP3YEHoJdVmFt-poXF8bj0JMS935-l4eoBuLZw2qNgI0bARyJvJ6cbH-9FM8vFrJALG47muTvtU43NKRe9-OHMa94_-GA1MZL2x_un9j-zEO-Xk9SHOiE41Wr1cuCC8Cu4tiX0sZWCxHoRjRtBFwSKaFKREvuWfnwC3Y31z9eSr0useQinwLUNoZitzDFI8x7e57acDpk-9c6ZznRnwyl-MwRNdJFH2MNh6nee1a77pHkjVyKc__Jm7KMzI95KM8mQuFd11W65KlF_rKdnjhDARUCiYfuSQqLvruFaoVePXsMqWQ29P33w-r3GeaAR_cLRCzeRa8BPeLkmm_cKDX-x11b_jSsx4Sz-9r7pnjLZBAeQ3hIiUAAHppfCJtKsjX_huhzQk3ErAwpIA196gREUC03p2Qb0zZJlq3WswissRVYVwc2fBPrPgH8HWrSexXFmkbJTZPWawIuDd32NBIWJyAHfY0ZyqXFFxA_uXw--2-IAvwDALCf454Yuq3mCnQesg55VPTAC6HWru6UftvyMEf7b1WXwnx6eVoqU9APxNPbGmc07hZpEZR4Gh2zplNY5i47AEIlSlWJw6yw-Je_wJ8APPaxfPj5J3UjGIDHCZ2Wwcd7JRncEZ1v4TYJU1ngOsTjJnBpVHwUZ8EeLOiZwZ-mDleg9J6pZjlkcfSdg=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-01T21:15:00.000Z", "utc_arrival": "2023-06-01T19:15:00.000Z", "local_departure": "2023-06-01T17:45:00.000Z", "utc_departure": "2023-06-01T15:45:00.000Z"}, {"id": "0b770a224c460000de3c5478_0|0a220b774c4a0000f5177ada_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 787.824685, "distance": 1975.87, "duration": {"departure": 12600, "return": 11700, "total": 24300}, "price": 241361.2975, "conversion": {"EUR": 631.825075, "HUF": 241361.2975}, "fare": {"adults": 120680.65, "children": 120680.65, "infants": 120680.65}, "bags_price": {"1": 123.242, "2": 246.47}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 439, "hold_height": 149, "hold_length": 171, "hold_weight": 20, "hold_width": 119, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 6}, "airlines": ["W6"], "route": [{"id": "0b770a224c460000de3c5478_0", "combination_id": "0b770a224c460000de3c5478", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "GHREG", "fare_category": "M", "fare_classes": "G", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-18T17:05:00.000Z", "utc_arrival": "2023-06-18T15:05:00.000Z", "local_departure": "2023-06-18T13:35:00.000Z", "utc_departure": "2023-06-18T11:35:00.000Z"}, {"id": "0a220b774c4a0000f5177ada_0", "combination_id": "0a220b774c4a0000f5177ada", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "JREG", "fare_category": "M", "fare_classes": "J", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-23T01:15:00.000Z", "utc_arrival": "2023-06-22T23:15:00.000Z", "local_departure": "2023-06-22T22:00:00.000Z", "utc_departure": "2023-06-22T20:00:00.000Z"}], "booking_token": "EFIQFOhG-8iWarSs_u9Y_xKIYL8sg8qKOFuXRH5eOcmMXn5UxUZCiNR8Wbcl5LP3rpItcr_jYYpF1qr2IaIQfLDMq05_D1CvK8JcmLT0QoREvEJ_jAdy6L-9nqpGijEy4eKRVZNL0zjGbhjm8Gq4RjNVIKNLcdPZ_-PWspQDdC27dyNy5FA63l6ISUzVpSmjX9eInwhi-FCuRVY7gZ_P5_iqZYHOI5V5Kq_NpNXMZ6VURiJeNsr0J5262j2zGZjxNtJZw_jPkp-c-yRfBiBlW5gPneoWz0W5_wBY2qAleblw39BOHugBl1gMXp27Qu83lk1qa79o5YLvY3k9fh3ndynsnvXuNpGMKgFQmdFakBOJ04svu0M4dtKJpKgF8DrQrtUyh5C9TkTsYs6iA0aDv19aPDOJuBRepaifcMCDQu5oYmHhHYzsYuDPb7bF59PCexIpiPeOD9CYI6eTQOvR0SQscc4B7QUhhUZlcm_D_sBZM6nlpsfYueDZcUdaep8-xSLAl2LtdKlqskJhv9por2TvzcOACRz1wZj1lwAdRQMUg1TQRaTAF2WXJ_KUFTexHOga7yawFWiDEiOkIN9_qNQHp-6l7xIiYahFGsqutxif9CGVV4RF23GeLnSRfANpXChAAboFt9y9zzYkKl9k6gir0654-fdq0VFoUwB6P7ENlPH-QcL5F9RqvKGXW7zfNBMi6KoxX95qbkoFNvPjX1U9NSj_afk-SCGkkPp3VlBODbinIRTku3CKlvmlr7dW8GqwYmIVFe5pPqAIN1bNBag==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c460000de3c5478_0%7C0a220b774c4a0000f5177ada_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EFIQFOhG-8iWarSs_u9Y_xKIYL8sg8qKOFuXRH5eOcmMXn5UxUZCiNR8Wbcl5LP3rpItcr_jYYpF1qr2IaIQfLDMq05_D1CvK8JcmLT0QoREvEJ_jAdy6L-9nqpGijEy4eKRVZNL0zjGbhjm8Gq4RjNVIKNLcdPZ_-PWspQDdC27dyNy5FA63l6ISUzVpSmjX9eInwhi-FCuRVY7gZ_P5_iqZYHOI5V5Kq_NpNXMZ6VURiJeNsr0J5262j2zGZjxNtJZw_jPkp-c-yRfBiBlW5gPneoWz0W5_wBY2qAleblw39BOHugBl1gMXp27Qu83lk1qa79o5YLvY3k9fh3ndynsnvXuNpGMKgFQmdFakBOJ04svu0M4dtKJpKgF8DrQrtUyh5C9TkTsYs6iA0aDv19aPDOJuBRepaifcMCDQu5oYmHhHYzsYuDPb7bF59PCexIpiPeOD9CYI6eTQOvR0SQscc4B7QUhhUZlcm_D_sBZM6nlpsfYueDZcUdaep8-xSLAl2LtdKlqskJhv9por2TvzcOACRz1wZj1lwAdRQMUg1TQRaTAF2WXJ_KUFTexHOga7yawFWiDEiOkIN9_qNQHp-6l7xIiYahFGsqutxif9CGVV4RF23GeLnSRfANpXChAAboFt9y9zzYkKl9k6gir0654-fdq0VFoUwB6P7ENlPH-QcL5F9RqvKGXW7zfNBMi6KoxX95qbkoFNvPjX1U9NSj_afk-SCGkkPp3VlBODbinIRTku3CKlvmlr7dW8GqwYmIVFe5pPqAIN1bNBag==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-18T17:05:00.000Z", "utc_arrival": "2023-06-18T15:05:00.000Z", "local_departure": "2023-06-18T13:35:00.000Z", "utc_departure": "2023-06-18T11:35:00.000Z"}, {"id": "0b770a224c240000ea08a5dc_0|0a220b774c28000046de2a57_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 792.115738, "distance": 1975.87, "duration": {"departure": 12000, "return": 12900, "total": 24900}, "price": 241981.8262, "conversion": {"EUR": 633.449468, "HUF": 241981.8262}, "fare": {"adults": 120990.91, "children": 120990.91, "infants": 120990.91}, "bags_price": {"1": 79.702, "2": 159.418}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 4}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224c240000ea08a5dc_0", "combination_id": "0b770a224c240000ea08a5dc", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-15T14:00:00.000Z", "utc_arrival": "2023-05-15T12:00:00.000Z", "local_departure": "2023-05-15T10:40:00.000Z", "utc_departure": "2023-05-15T08:40:00.000Z"}, {"id": "0a220b774c28000046de2a57_0", "combination_id": "0a220b774c28000046de2a57", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "JKREG", "fare_category": "M", "fare_classes": "J", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-20T00:05:00.000Z", "utc_arrival": "2023-05-19T22:05:00.000Z", "local_departure": "2023-05-19T20:30:00.000Z", "utc_departure": "2023-05-19T18:30:00.000Z"}], "booking_token": "EqKx45T8-jq99lEmYLpfuvnAz2knL29PAnUSg-6ETJ10aoSasIkSOwihU9azefLkiIqM58lllrZWkN9Ybj5WeZQDgpVuZye_hFfz_e9_JCas1_XEN7jzUV1wsrdgnDHzFir1c-ToAfx6FNs95XydKfr49g1KEnT5QgIf6layHbo1AaN0QyQEVdMsQQtorSScdQMNMEUrkaoKtNzqAbyUaSOmSgOADFD6rDs4bSwxZ2GqjbkCk5ALqmZIqQlklMYn-Jz99VnwtaIhaVxGgukYoodqFKHjoNcsqkzDl-pLtDr3jWeWygH05FNsB6JbNM1wKnwbfSBcLhF2LSwLLEqvpwPIvq1K9a85OdUX90ny5gUSasUYh2G2gwHjMrcZ37aiGF10z2hnNngRTWOF_Gfzzw6Fy1N60eJk-h0f3fQFUZJldWVY4ucF6TkL9SQ_j9xHoUsHgrOBS78symNXFUTJDO8U-dCGVJ2SL9ABs0R2KrveRP9q2Oaps33Qp66dlaIIy_IkaS63MLAaKD1vBoYYcaAWS6DJhwrxcHCzQdksbjes3C5QDJScIDOQ-MrrVa8uOhzxzpGevZh4WLtE7En29B8hmEFLicAoI9PXmPePXw9qlriu4T1CKwF2Sz4zG9-vMaQ0G_KZcfYExB0DfikNvpHJe9DhzeUzs4KXaJPDB3x-467g_j0nWX3kiCzOVEgAKisDqXLu652AjdSXaj2xpIvRKafncc2Rb8QoVk5gcG5SX-OqCYSFhyBxWsfY5BpgGpibZwWphnPQVBd7NjrLvig==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c240000ea08a5dc_0%7C0a220b774c28000046de2a57_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EqKx45T8-jq99lEmYLpfuvnAz2knL29PAnUSg-6ETJ10aoSasIkSOwihU9azefLkiIqM58lllrZWkN9Ybj5WeZQDgpVuZye_hFfz_e9_JCas1_XEN7jzUV1wsrdgnDHzFir1c-ToAfx6FNs95XydKfr49g1KEnT5QgIf6layHbo1AaN0QyQEVdMsQQtorSScdQMNMEUrkaoKtNzqAbyUaSOmSgOADFD6rDs4bSwxZ2GqjbkCk5ALqmZIqQlklMYn-Jz99VnwtaIhaVxGgukYoodqFKHjoNcsqkzDl-pLtDr3jWeWygH05FNsB6JbNM1wKnwbfSBcLhF2LSwLLEqvpwPIvq1K9a85OdUX90ny5gUSasUYh2G2gwHjMrcZ37aiGF10z2hnNngRTWOF_Gfzzw6Fy1N60eJk-h0f3fQFUZJldWVY4ucF6TkL9SQ_j9xHoUsHgrOBS78symNXFUTJDO8U-dCGVJ2SL9ABs0R2KrveRP9q2Oaps33Qp66dlaIIy_IkaS63MLAaKD1vBoYYcaAWS6DJhwrxcHCzQdksbjes3C5QDJScIDOQ-MrrVa8uOhzxzpGevZh4WLtE7En29B8hmEFLicAoI9PXmPePXw9qlriu4T1CKwF2Sz4zG9-vMaQ0G_KZcfYExB0DfikNvpHJe9DhzeUzs4KXaJPDB3x-467g_j0nWX3kiCzOVEgAKisDqXLu652AjdSXaj2xpIvRKafncc2Rb8QoVk5gcG5SX-OqCYSFhyBxWsfY5BpgGpibZwWphnPQVBd7NjrLvig==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-15T14:00:00.000Z", "utc_arrival": "2023-05-15T12:00:00.000Z", "local_departure": "2023-05-15T10:40:00.000Z", "utc_departure": "2023-05-15T08:40:00.000Z"}, {"id": "0b770a224c2e00002007cc72_0|0a220b774c320000e133d3ca_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 785.278482, "distance": 1975.87, "duration": {"departure": 11700, "return": 11400, "total": 23100}, "price": 242425.9944, "conversion": {"EUR": 634.612192, "HUF": 242425.9944}, "fare": {"adults": 121213, "children": 121213, "infants": 121213}, "bags_price": {"1": 73.486, "2": 156.772}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 158, "hold_height": 52, "hold_length": 78, "hold_weight": 20, "hold_width": 28, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 3, "personal_item_width": 15}, "availability": {"seats": 3}, "airlines": ["FR", "VY"], "route": [{"id": "0b770a224c2e00002007cc72_0", "combination_id": "0b770a224c2e00002007cc72", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "VY", "flight_no": 5193, "operating_carrier": "IB", "operating_flight_no": "3279", "fare_basis": "WNBBLJA", "fare_category": "M", "fare_classes": "W", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-25T18:50:00.000Z", "utc_arrival": "2023-05-25T16:50:00.000Z", "local_departure": "2023-05-25T15:35:00.000Z", "utc_departure": "2023-05-25T13:35:00.000Z"}, {"id": "0a220b774c320000e133d3ca_0", "combination_id": "0a220b774c320000e133d3ca", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-29T10:15:00.000Z", "utc_arrival": "2023-05-29T08:15:00.000Z", "local_departure": "2023-05-29T07:05:00.000Z", "utc_departure": "2023-05-29T05:05:00.000Z"}], "booking_token": "EnUQEP5Gj9sPYrHpiQD2y65vJOmU2vM0RqjtcvI9F_nDRRVevv84JrndIKFp19lGC6dDY3v4bqdisPSqP_HuKRlaYQhi5jHBm7HcXzKK1cYJvQT6FC2df3D3gCoGWk7xGfNNobxYGCHXxTgogbj8qWzlRv2o8brMISt924EG-LUxWk4jr66gJKIb-3sEsH6PiAoGpYj73wunKNkSNRatUH6j9R27WoDnGGqNIBoOZwqhEXt_IlZXX5pXDNNIrwQajuAIbL3GS5co9i7aXOwy3gi_N_0WdNHyan75vN79O7xENywdpSxNjGy8ICqrwuJZv1r7eQv8ia1Y1I3GnsZGbidBDGi8WfAZKP4iDYN74TV3zxYLqMbrIDt9sy2NZ81qoDc_nALMpg_Xqo5_1yA_IU4Wcb0htdAHgTVnYW-CIgtwlhzb_5_JCACZ-hSyPj53srv48yW4upaGY2R2QjE7WuygVi6-pCKjLUvQjkHAJkIrzcM6Nis8zIXQTOAG_oyZuZkdx2E-V_iPbzte_j46UCSTr0ZJozi1tDn69MK-eG1cJjIhaKPyW49e0aDeARrNS7dkpzbkpGBG_s0FfFCYDSMwKz49Y73M42vvhtbKfgtz8WjxkDF-9W47j9zU9Kn4TvF9U2djlb1NkEiC6P4h8mDJg14nxBPvCo9VlNvEZUAp-yxo01OMW3dMMIm3GG4Mb1qDSqmSwxFr0k-mVq2NGVbu9FnA9ZCceIQhcPQENfxq1_LiKtFbVqZzxl3qmwAKc", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c2e00002007cc72_0%7C0a220b774c320000e133d3ca_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EnUQEP5Gj9sPYrHpiQD2y65vJOmU2vM0RqjtcvI9F_nDRRVevv84JrndIKFp19lGC6dDY3v4bqdisPSqP_HuKRlaYQhi5jHBm7HcXzKK1cYJvQT6FC2df3D3gCoGWk7xGfNNobxYGCHXxTgogbj8qWzlRv2o8brMISt924EG-LUxWk4jr66gJKIb-3sEsH6PiAoGpYj73wunKNkSNRatUH6j9R27WoDnGGqNIBoOZwqhEXt_IlZXX5pXDNNIrwQajuAIbL3GS5co9i7aXOwy3gi_N_0WdNHyan75vN79O7xENywdpSxNjGy8ICqrwuJZv1r7eQv8ia1Y1I3GnsZGbidBDGi8WfAZKP4iDYN74TV3zxYLqMbrIDt9sy2NZ81qoDc_nALMpg_Xqo5_1yA_IU4Wcb0htdAHgTVnYW-CIgtwlhzb_5_JCACZ-hSyPj53srv48yW4upaGY2R2QjE7WuygVi6-pCKjLUvQjkHAJkIrzcM6Nis8zIXQTOAG_oyZuZkdx2E-V_iPbzte_j46UCSTr0ZJozi1tDn69MK-eG1cJjIhaKPyW49e0aDeARrNS7dkpzbkpGBG_s0FfFCYDSMwKz49Y73M42vvhtbKfgtz8WjxkDF-9W47j9zU9Kn4TvF9U2djlb1NkEiC6P4h8mDJg14nxBPvCo9VlNvEZUAp-yxo01OMW3dMMIm3GG4Mb1qDSqmSwxFr0k-mVq2NGVbu9FnA9ZCceIQhcPQENfxq1_LiKtFbVqZzxl3qmwAKc", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-25T18:50:00.000Z", "utc_arrival": "2023-05-25T16:50:00.000Z", "local_departure": "2023-05-25T15:35:00.000Z", "utc_departure": "2023-05-25T13:35:00.000Z"}, {"id": "0b770a224bf30000aac9af64_0|0a220b774bf600003991cd2d_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 788.341597, "distance": 1975.87, "duration": {"departure": 12000, "return": 11700, "total": 23700}, "price": 242577.4428, "conversion": {"EUR": 635.008647, "HUF": 242577.4428}, "fare": {"adults": 121288.72, "children": 121288.72, "infants": 121288.72}, "bags_price": {"1": 81.312, "2": 162.624}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 3}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224bf30000aac9af64_0", "combination_id": "0b770a224bf30000aac9af64", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-03-27T14:00:00.000Z", "utc_arrival": "2023-03-27T12:00:00.000Z", "local_departure": "2023-03-27T10:40:00.000Z", "utc_departure": "2023-03-27T08:40:00.000Z"}, {"id": "0a220b774bf600003991cd2d_0", "combination_id": "0a220b774bf600003991cd2d", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "GHREG", "fare_category": "M", "fare_classes": "G", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-03-31T01:15:00.000Z", "utc_arrival": "2023-03-30T23:15:00.000Z", "local_departure": "2023-03-30T22:00:00.000Z", "utc_departure": "2023-03-30T20:00:00.000Z"}], "booking_token": "EDUeKVcdpeP1V0BpSzRIfoNm1PM_W8pgkGnQqD4i9BfhivJ3bLlB4_lkiFSKf3Z-s9IUIbQwO-cZuaOW2u1d8ZHnbk8JppNKObGhFt1eQwBZZ_1xNQBoNJP-e2Wk0ua0HzrEWOx-cA5cO04mCOa1gPnwh1b4QF6uAkenHn-TA1DZH3A7SLVm2YCz7OCV__2OqmGORQG__SL8UKUoo4TyZpPvAFHe64Way21fBjOd1jFqbazlo2sx7jHhii1WXTYAvURwfKkXBq1XhD5Mhcy2QPW9HoOO5G-fdQekzd2yQsOBkTIKLna11XmTjDwbeNbm20C0glDH73PeF-mvdW63O6q9IUg_FLBTLmITgV4B4GmYgOUOWhckmFlPWI3Ex96cVUdyXz9SQETZtAlul149jFcCjFUF5HnnZaewKi2fSD0iCzn6uI9YyoOF_c5s5cD7KesITgj11pZJ4nRbqFRVsJc6ozA7mBlmL-Cc-0Nbt6beEchbEOUV--gDEN1Ju0aEQ3K-_MoO_lVL6lisIokAHyk7--7M4G2DTILL78MRyNrqVEqxNYNx3n4OHKRbvQtzZ_Ok1VtbEEhzO3P_mUiCIuWw0DvNq-USjkGRjO5omd0RJUB99Af0NTnIX6snjIaKmkkDqmi_ai0iB7BNPHWKqY1a-TrJrbicLCffIc_7WmlR6g9TB-HHZhb9SV0peztilfpWdQbqUjO9aZ83CY6-ON58yOyIIvbLYDhCoVczQhbSlxIvxQHQnRzKXaMMLwKcgNWTAGC85P1PVAsnQEe-SG7tgiBejiyEHFTOCWzG67es=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224bf30000aac9af64_0%7C0a220b774bf600003991cd2d_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EDUeKVcdpeP1V0BpSzRIfoNm1PM_W8pgkGnQqD4i9BfhivJ3bLlB4_lkiFSKf3Z-s9IUIbQwO-cZuaOW2u1d8ZHnbk8JppNKObGhFt1eQwBZZ_1xNQBoNJP-e2Wk0ua0HzrEWOx-cA5cO04mCOa1gPnwh1b4QF6uAkenHn-TA1DZH3A7SLVm2YCz7OCV__2OqmGORQG__SL8UKUoo4TyZpPvAFHe64Way21fBjOd1jFqbazlo2sx7jHhii1WXTYAvURwfKkXBq1XhD5Mhcy2QPW9HoOO5G-fdQekzd2yQsOBkTIKLna11XmTjDwbeNbm20C0glDH73PeF-mvdW63O6q9IUg_FLBTLmITgV4B4GmYgOUOWhckmFlPWI3Ex96cVUdyXz9SQETZtAlul149jFcCjFUF5HnnZaewKi2fSD0iCzn6uI9YyoOF_c5s5cD7KesITgj11pZJ4nRbqFRVsJc6ozA7mBlmL-Cc-0Nbt6beEchbEOUV--gDEN1Ju0aEQ3K-_MoO_lVL6lisIokAHyk7--7M4G2DTILL78MRyNrqVEqxNYNx3n4OHKRbvQtzZ_Ok1VtbEEhzO3P_mUiCIuWw0DvNq-USjkGRjO5omd0RJUB99Af0NTnIX6snjIaKmkkDqmi_ai0iB7BNPHWKqY1a-TrJrbicLCffIc_7WmlR6g9TB-HHZhb9SV0peztilfpWdQbqUjO9aZ83CY6-ON58yOyIIvbLYDhCoVczQhbSlxIvxQHQnRzKXaMMLwKcgNWTAGC85P1PVAsnQEe-SG7tgiBejiyEHFTOCWzG67es=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-03-27T14:00:00.000Z", "utc_arrival": "2023-03-27T12:00:00.000Z", "local_departure": "2023-03-27T10:40:00.000Z", "utc_departure": "2023-03-27T08:40:00.000Z"}, {"id": "0b770a224bed00002550d810_0|0a220b774bf10000f0b20103_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 788.503477, "distance": 1975.87, "duration": {"departure": 12000, "return": 11700, "total": 23700}, "price": 242639.282, "conversion": {"EUR": 635.170527, "HUF": 242639.282}, "fare": {"adults": 121319.64, "children": 121319.64, "infants": 121319.64}, "bags_price": {"1": 86.52, "2": 173.054}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 6}, "airlines": ["FR"], "route": [{"id": "0b770a224bed00002550d810_0", "combination_id": "0b770a224bed00002550d810", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-03-21T19:50:00.000Z", "utc_arrival": "2023-03-21T18:50:00.000Z", "local_departure": "2023-03-21T16:30:00.000Z", "utc_departure": "2023-03-21T15:30:00.000Z"}, {"id": "0a220b774bf10000f0b20103_0", "combination_id": "0a220b774bf10000f0b20103", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6709, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-03-25T18:05:00.000Z", "utc_arrival": "2023-03-25T17:05:00.000Z", "local_departure": "2023-03-25T14:50:00.000Z", "utc_departure": "2023-03-25T13:50:00.000Z"}], "booking_token": "E5INB4STJCVAWJ4bcR1rbd_3vnW1Tp9wtcJ-NgL1xdH6DRE2EjD8-W5eIIfc_qIq3SL6CRKA0z4T05sNWT4qgYz_8IhmDyFIR8auZG-o1huS2xii5krZxXFTpa90pXsySTngmnMRYktf4HJ_z6Nw_ClOWSiZqr44PdvpFyYlEpgF9wBtYmNI7wRBAwrg6FuXZ-TMWXws9E19s57l2OjEg_sX-JiGYwrCKhxA4DLwyWw8wTlOqFTYD08mz9VFV3xsvc6A4rtyxTiMRNbiaZVpAfcZe9cGrZO18wRgiBGKmh8UwzuIzhZvOmYKW1Ce2iBY4oIH-lhb82Kcpln8SZzUa1AlhBhPVJj0VH-WHzMOB5DBfy7HOqVnSyCAHasY2mieCY-0d4rHXJfqFMBh6HiR8hpapYNtlrS7w0fmj9C1QsSAX4thrbPsMoyPCuj1j9PuRUaNK7JWo5W2s7Ym2068RAwcoslXcREt-kl4ZEV95bisFwHNwmIa64eoP4xKHUZL38jSVQXPjdpcbOJ4AaKN0Z1D0oRJxrCk_Z4m-M1X05GSum_aP4wop4ow9g3sekK33bGCbcvUCs-sgUmAXiP8nqr-h9PDugL2Mds1ZzpnLcuTuR2j2BNGPSHzRPxNnMtnpxo9U43PVmjKFzwDEKc0OxrVwpg288JjbWNNBBY7qcPW9e_zzZNNJQ8cBXbbbDaKXG3Jmb_lpMjngCLLfPwEEzdiqfkfdCgVY4NMTJKeSH64=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224bed00002550d810_0%7C0a220b774bf10000f0b20103_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=E5INB4STJCVAWJ4bcR1rbd_3vnW1Tp9wtcJ-NgL1xdH6DRE2EjD8-W5eIIfc_qIq3SL6CRKA0z4T05sNWT4qgYz_8IhmDyFIR8auZG-o1huS2xii5krZxXFTpa90pXsySTngmnMRYktf4HJ_z6Nw_ClOWSiZqr44PdvpFyYlEpgF9wBtYmNI7wRBAwrg6FuXZ-TMWXws9E19s57l2OjEg_sX-JiGYwrCKhxA4DLwyWw8wTlOqFTYD08mz9VFV3xsvc6A4rtyxTiMRNbiaZVpAfcZe9cGrZO18wRgiBGKmh8UwzuIzhZvOmYKW1Ce2iBY4oIH-lhb82Kcpln8SZzUa1AlhBhPVJj0VH-WHzMOB5DBfy7HOqVnSyCAHasY2mieCY-0d4rHXJfqFMBh6HiR8hpapYNtlrS7w0fmj9C1QsSAX4thrbPsMoyPCuj1j9PuRUaNK7JWo5W2s7Ym2068RAwcoslXcREt-kl4ZEV95bisFwHNwmIa64eoP4xKHUZL38jSVQXPjdpcbOJ4AaKN0Z1D0oRJxrCk_Z4m-M1X05GSum_aP4wop4ow9g3sekK33bGCbcvUCs-sgUmAXiP8nqr-h9PDugL2Mds1ZzpnLcuTuR2j2BNGPSHzRPxNnMtnpxo9U43PVmjKFzwDEKc0OxrVwpg288JjbWNNBBY7qcPW9e_zzZNNJQ8cBXbbbDaKXG3Jmb_lpMjngCLLfPwEEzdiqfkfdCgVY4NMTJKeSH64=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-03-21T19:50:00.000Z", "utc_arrival": "2023-03-21T18:50:00.000Z", "local_departure": "2023-03-21T16:30:00.000Z", "utc_departure": "2023-03-21T15:30:00.000Z"}, {"id": "0b770a224c4a00006b86e63f_0|0a220b774c4e0000de14d559_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 791.740452, "distance": 1975.87, "duration": {"departure": 12600, "return": 11700, "total": 24300}, "price": 242857.146, "conversion": {"EUR": 635.740842, "HUF": 242857.146}, "fare": {"adults": 121428.57, "children": 128167.94, "infants": 128167.94}, "bags_price": {"1": 123.242, "2": 246.47}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 439, "hold_height": 149, "hold_length": 171, "hold_weight": 20, "hold_width": 119, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 7}, "airlines": ["W6"], "route": [{"id": "0b770a224c4a00006b86e63f_0", "combination_id": "0b770a224c4a00006b86e63f", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "HREG", "fare_category": "M", "fare_classes": "H", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-22T21:15:00.000Z", "utc_arrival": "2023-06-22T19:15:00.000Z", "local_departure": "2023-06-22T17:45:00.000Z", "utc_departure": "2023-06-22T15:45:00.000Z"}, {"id": "0a220b774c4e0000de14d559_0", "combination_id": "0a220b774c4e0000de14d559", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IJREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-26T23:45:00.000Z", "utc_arrival": "2023-06-26T21:45:00.000Z", "local_departure": "2023-06-26T20:30:00.000Z", "utc_departure": "2023-06-26T18:30:00.000Z"}], "booking_token": "EwBeGU7x-li_T8gqL5N3MAYfy4OJN70Z-4cQcA36OxHTZraXWoUrNeS35H0d8LG9kfYmhTi0NZfmbE1nM4boUJ82XU5xUZZzmuVxyQwVsUY6_e6xVE7WGaYISf4oh2EugtisZ_99NdHbIOobkeIlt7zmVuHwD3-gceLnPw-WDe8vnrtDf849RnJayblJysrKl212-wSNLZI0Fhta94TrtFBRCog8fpwEMBolWyLD_rGO2fZD0GsvUpLOEzcCzC0GXSd6gl2Pkw9wf64A7v5GOlZt8KP5syD1U3ujECvcQM-leIGuvKElFZGDiVF6AnZmm009DV5ZUe602OtQLc1Ky5ocZHxzFA-dDdIwbPDpBnJ3RhjUkCmm_dSvairv92lwzRFRRaTN120SwIn7j1LFyM6Z8qBfdWkkUSo8rIIsQCKJtDUPexPhGyj2izJ68y4PHN-WzomTsy8qjMuJ-3Bkk3iAAJ4r5-sVmvvm4KTKZFGNa7gniIR_dMpJWLxd_FdV5PKKPpihCU01IpU-GBGMroW79x2279F9If5a1WDGoiM6dXERkDJEOttEGTnQ1-k7uPRZnmCLxOrJm7LEw4Lp0bYJRtiQyE0lP_X51HuQ1de_-eUgdGJuPrLpeqz55azcn23W813U8Tl_IhvMxT1shoi4OVFOMtd4lf7v-a4SY74ulir2momFziuwnpmQrVVYxw66yVScgx1xNqCvhCEW1tI6JR2RMdyZF6MkVwQ1LTlXSfQYuvm5ndxRg9RsVNbSLclecJdQHIRViT9n63wneVYD6G2tmodIYgFQD-k_ENrs=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c4a00006b86e63f_0%7C0a220b774c4e0000de14d559_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EwBeGU7x-li_T8gqL5N3MAYfy4OJN70Z-4cQcA36OxHTZraXWoUrNeS35H0d8LG9kfYmhTi0NZfmbE1nM4boUJ82XU5xUZZzmuVxyQwVsUY6_e6xVE7WGaYISf4oh2EugtisZ_99NdHbIOobkeIlt7zmVuHwD3-gceLnPw-WDe8vnrtDf849RnJayblJysrKl212-wSNLZI0Fhta94TrtFBRCog8fpwEMBolWyLD_rGO2fZD0GsvUpLOEzcCzC0GXSd6gl2Pkw9wf64A7v5GOlZt8KP5syD1U3ujECvcQM-leIGuvKElFZGDiVF6AnZmm009DV5ZUe602OtQLc1Ky5ocZHxzFA-dDdIwbPDpBnJ3RhjUkCmm_dSvairv92lwzRFRRaTN120SwIn7j1LFyM6Z8qBfdWkkUSo8rIIsQCKJtDUPexPhGyj2izJ68y4PHN-WzomTsy8qjMuJ-3Bkk3iAAJ4r5-sVmvvm4KTKZFGNa7gniIR_dMpJWLxd_FdV5PKKPpihCU01IpU-GBGMroW79x2279F9If5a1WDGoiM6dXERkDJEOttEGTnQ1-k7uPRZnmCLxOrJm7LEw4Lp0bYJRtiQyE0lP_X51HuQ1de_-eUgdGJuPrLpeqz55azcn23W813U8Tl_IhvMxT1shoi4OVFOMtd4lf7v-a4SY74ulir2momFziuwnpmQrVVYxw66yVScgx1xNqCvhCEW1tI6JR2RMdyZF6MkVwQ1LTlXSfQYuvm5ndxRg9RsVNbSLclecJdQHIRViT9n63wneVYD6G2tmodIYgFQD-k_ENrs=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-22T21:15:00.000Z", "utc_arrival": "2023-06-22T19:15:00.000Z", "local_departure": "2023-06-22T17:45:00.000Z", "utc_departure": "2023-06-22T15:45:00.000Z"}, {"id": "0b770a224c4b000059b2d558_0|0a220b774c4e00006fcb60de_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 789.188764, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 243410.4068, "conversion": {"EUR": 637.189144, "HUF": 243410.4068}, "fare": {"adults": 121705.2, "children": 121705.2, "infants": 121705.2}, "bags_price": {"1": 79.212, "2": 168.224}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 158, "hold_height": 52, "hold_length": 78, "hold_weight": 20, "hold_width": 28, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 3, "personal_item_width": 15}, "availability": {"seats": 3}, "airlines": ["FR", "IB"], "route": [{"id": "0b770a224c4b000059b2d558_0", "combination_id": "0b770a224c4b000059b2d558", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-23T21:45:00.000Z", "utc_arrival": "2023-06-23T19:45:00.000Z", "local_departure": "2023-06-23T18:25:00.000Z", "utc_departure": "2023-06-23T16:25:00.000Z"}, {"id": "0a220b774c4e00006fcb60de_0", "combination_id": "0a220b774c4e00006fcb60de", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "IB", "flight_no": 3278, "operating_carrier": "IB", "operating_flight_no": "3278", "fare_basis": "SDNNAOB4", "fare_category": "M", "fare_classes": "S", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-26T14:55:00.000Z", "utc_arrival": "2023-06-26T12:55:00.000Z", "local_departure": "2023-06-26T11:45:00.000Z", "utc_departure": "2023-06-26T09:45:00.000Z"}], "booking_token": "Ek6XEC7KXcnCZQtKs017S4pnFPJ7gF89LIDDn1IRNnjS-BCK0ukJhbQcvNJpgj1CKtj3BL7SL-9V0FmPKFW1AVn46Y3ieWUSKLudy2s0mE5435oD55k83T9L6x2taxMfqqip4BX0W0lclC4bfBZHfayNcCUIHumOFAQXDr0yWs0SYfKvUBSlJKX81opl1MviDkwqiJ9Lh3stkgYzOvGJ3PtP6Xk1-2bnJCPATMQxnRrvVTm87CpqUmganpFNLt7TqjrpcKe40_4xT2zFpCmCtPJWUcTjNRhFh8NmroK_rjrK47xDM_F1JgzNaie2eoLGH4Ge9oyP1MR73f7rD2jWxiM0N0s469xWlVkdOvlKbLziAGiyjaEhk_9-MBIJOSSxQz-Y1jiAFefQEHaJ3WMME3vmVTqQLZYeMj9XVkA1y6sAZOBwPK8wF0EO88F6RmqVfUnCE9k-m_cC159D9lOjVt_rBQM17_q8dcbk__IVo9zjgrUN8Y-xCn7fkxH_O18MlNvplRtl3VAVb5vdZY8z782EgZYBoPaOj8FLByZetW0czQGfZ1mDrjpGRp-xVg2vrmS3vAOoIjNw1cZTGWuLHP_VbXfepM426wNxPqSVAJZ-qZmZ29MES1-JwQo6bDSkCs899VNCPg3bkTRmlmGdmloDklQfkHoguGtG1FO98yXgSTA1Y238D4muMlEQ_2csX_bgObKgqprsXXtWoD0-mTBmdfVd82vU3-fM1UWYXvyTxpNfzwPhE5z-w_SSzRqBjK_mREdBt1WkXL8fDxovYyJuijaGPuuIk3Bg_D9Gge9SaDj40YtUsiUeCsKPsOdgH", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c4b000059b2d558_0%7C0a220b774c4e00006fcb60de_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=Ek6XEC7KXcnCZQtKs017S4pnFPJ7gF89LIDDn1IRNnjS-BCK0ukJhbQcvNJpgj1CKtj3BL7SL-9V0FmPKFW1AVn46Y3ieWUSKLudy2s0mE5435oD55k83T9L6x2taxMfqqip4BX0W0lclC4bfBZHfayNcCUIHumOFAQXDr0yWs0SYfKvUBSlJKX81opl1MviDkwqiJ9Lh3stkgYzOvGJ3PtP6Xk1-2bnJCPATMQxnRrvVTm87CpqUmganpFNLt7TqjrpcKe40_4xT2zFpCmCtPJWUcTjNRhFh8NmroK_rjrK47xDM_F1JgzNaie2eoLGH4Ge9oyP1MR73f7rD2jWxiM0N0s469xWlVkdOvlKbLziAGiyjaEhk_9-MBIJOSSxQz-Y1jiAFefQEHaJ3WMME3vmVTqQLZYeMj9XVkA1y6sAZOBwPK8wF0EO88F6RmqVfUnCE9k-m_cC159D9lOjVt_rBQM17_q8dcbk__IVo9zjgrUN8Y-xCn7fkxH_O18MlNvplRtl3VAVb5vdZY8z782EgZYBoPaOj8FLByZetW0czQGfZ1mDrjpGRp-xVg2vrmS3vAOoIjNw1cZTGWuLHP_VbXfepM426wNxPqSVAJZ-qZmZ29MES1-JwQo6bDSkCs899VNCPg3bkTRmlmGdmloDklQfkHoguGtG1FO98yXgSTA1Y238D4muMlEQ_2csX_bgObKgqprsXXtWoD0-mTBmdfVd82vU3-fM1UWYXvyTxpNfzwPhE5z-w_SSzRqBjK_mREdBt1WkXL8fDxovYyJuijaGPuuIk3Bg_D9Gge9SaDj40YtUsiUeCsKPsOdgH", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-23T21:45:00.000Z", "utc_arrival": "2023-06-23T19:45:00.000Z", "local_departure": "2023-06-23T18:25:00.000Z", "utc_departure": "2023-06-23T16:25:00.000Z"}, {"id": "0b770a224c280000cced2481_0|0a220b774c2b0000f0938698_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 790.748347, "distance": 1975.87, "duration": {"departure": 12000, "return": 11700, "total": 23700}, "price": 243496.837, "conversion": {"EUR": 637.415397, "HUF": 243496.837}, "fare": {"adults": 121748.42, "children": 121748.42, "infants": 121748.42}, "bags_price": {"1": 75.796, "2": 151.592}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 4}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224c280000cced2481_0", "combination_id": "0b770a224c280000cced2481", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-19T21:45:00.000Z", "utc_arrival": "2023-05-19T19:45:00.000Z", "local_departure": "2023-05-19T18:25:00.000Z", "utc_departure": "2023-05-19T16:25:00.000Z"}, {"id": "0a220b774c2b0000f0938698_0", "combination_id": "0a220b774c2b0000f0938698", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "HREG", "fare_category": "M", "fare_classes": "H", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-22T23:45:00.000Z", "utc_arrival": "2023-05-22T21:45:00.000Z", "local_departure": "2023-05-22T20:30:00.000Z", "utc_departure": "2023-05-22T18:30:00.000Z"}], "booking_token": "E-eA9RIU2I-ss_Yd-KeL53g-Y4DKVJt7KdPJT6vHJBuAE2klj_zYe7xvwqZNE0fI5Kk7YsGMYqBlLQBy5rtDmjS_POhIQ4HkOajC6OXzwdhFxqS4mvWXIvSkF63yY7Ydxfw_wdX4o4nu6oUPsmHFrpe_hIcFosJVNgv-yg426S_WWe6Da16FLOMGa0xMKR6NJnJtMHpPcKJdavZTu4t_OB3Fe6cYX6qLmfaXpLUmxA_ur_SnCIz-fmLtRja70M3rHWCEaLtUAOPaA-B9kLMbkWulYFCxvSRIH96m9oPcN98L1Xz0VGrmkWspHl4cIg0DTDwSuBik8raV9fGsSy_fVn0mmy0DhU4CUKwm4uj1qkyjYMLfVw8kMPBNBgSyE-spmqWcneCctCCK-xnEvmCMzivdKBzYcfvd7CkDC_aALUzcwHZzYHC8NYFdHJfif7ZG3ovgXQ-wa6QLUQxxl86-woV7xAxAGs67tyX54eYgFwfrf6ysuAqHXlSEVLxaVwt2986Qqxi59R13HeL0gGpBi1JcjGZfGt6kNRzD05b-KNPn_pEWsNMdhMLoHTwph4gbNqRU_TQpWewqQ8uQYRO0NjenX0MeP0AkcmvME0w4PZcbj3IO8hluOjcHIZjCkM2_oXB7mtuGpa-pVPE_aYSMpWE0DrOp7rNod3NzxJ1g3m75OKCT-rl-PGkDEuvp5tSZiiBECW5aSK8IOj72eUOVFgvJOpSoNfNzatYsgHzgv3rhOOjKpLZkc0PSkGIXORMCPr3_JAgcWH0BHRYiFTtcDVA==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c280000cced2481_0%7C0a220b774c2b0000f0938698_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=E-eA9RIU2I-ss_Yd-KeL53g-Y4DKVJt7KdPJT6vHJBuAE2klj_zYe7xvwqZNE0fI5Kk7YsGMYqBlLQBy5rtDmjS_POhIQ4HkOajC6OXzwdhFxqS4mvWXIvSkF63yY7Ydxfw_wdX4o4nu6oUPsmHFrpe_hIcFosJVNgv-yg426S_WWe6Da16FLOMGa0xMKR6NJnJtMHpPcKJdavZTu4t_OB3Fe6cYX6qLmfaXpLUmxA_ur_SnCIz-fmLtRja70M3rHWCEaLtUAOPaA-B9kLMbkWulYFCxvSRIH96m9oPcN98L1Xz0VGrmkWspHl4cIg0DTDwSuBik8raV9fGsSy_fVn0mmy0DhU4CUKwm4uj1qkyjYMLfVw8kMPBNBgSyE-spmqWcneCctCCK-xnEvmCMzivdKBzYcfvd7CkDC_aALUzcwHZzYHC8NYFdHJfif7ZG3ovgXQ-wa6QLUQxxl86-woV7xAxAGs67tyX54eYgFwfrf6ysuAqHXlSEVLxaVwt2986Qqxi59R13HeL0gGpBi1JcjGZfGt6kNRzD05b-KNPn_pEWsNMdhMLoHTwph4gbNqRU_TQpWewqQ8uQYRO0NjenX0MeP0AkcmvME0w4PZcbj3IO8hluOjcHIZjCkM2_oXB7mtuGpa-pVPE_aYSMpWE0DrOp7rNod3NzxJ1g3m75OKCT-rl-PGkDEuvp5tSZiiBECW5aSK8IOj72eUOVFgvJOpSoNfNzatYsgHzgv3rhOOjKpLZkc0PSkGIXORMCPr3_JAgcWH0BHRYiFTtcDVA==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-19T21:45:00.000Z", "utc_arrival": "2023-05-19T19:45:00.000Z", "local_departure": "2023-05-19T18:25:00.000Z", "utc_departure": "2023-05-19T16:25:00.000Z"}, {"id": "0b770a224c0800005e1413f9_0|0a220b774c0b00004bb09d25_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 793.736422, "distance": 1975.87, "duration": {"departure": 12600, "return": 11700, "total": 24300}, "price": 243619.6196, "conversion": {"EUR": 637.736812, "HUF": 243619.6196}, "fare": {"adults": 121809.81, "children": 125469.3, "infants": 125469.3}, "bags_price": {"1": 126.224, "2": 252.434}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 439, "hold_height": 149, "hold_length": 171, "hold_weight": 20, "hold_width": 119, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 3}, "airlines": ["W6"], "route": [{"id": "0b770a224c0800005e1413f9_0", "combination_id": "0b770a224c0800005e1413f9", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "JREG", "fare_category": "M", "fare_classes": "J", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-17T19:45:00.000Z", "utc_arrival": "2023-04-17T17:45:00.000Z", "local_departure": "2023-04-17T16:15:00.000Z", "utc_departure": "2023-04-17T14:15:00.000Z"}, {"id": "0a220b774c0b00004bb09d25_0", "combination_id": "0a220b774c0b00004bb09d25", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "HIREG", "fare_category": "M", "fare_classes": "H", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-21T01:15:00.000Z", "utc_arrival": "2023-04-20T23:15:00.000Z", "local_departure": "2023-04-20T22:00:00.000Z", "utc_departure": "2023-04-20T20:00:00.000Z"}], "booking_token": "EF45_3bCa1rkH2JW2NxmZl0h3RA-1Rp_hK4OpC9lbrMo0b7fjs98If2_oPbtM-SUyl8yWzY839EBWeQ4eqmhU9L4RFerR5lvz1JDgmc06OKUD-ZmGeAyaAicUUf10TrdFIOer09Kpr3Arqh7bHshwD4GSMPQrOGx1316M21W76majUPJ0PPX1NFsRHDunELqmXOozp7jIcWYa3l1WjHVAe0rCLBEPKmqI34VB5qhGeaH0FBE-BK3VZ9fQjal2bBO8wTOs0CxCFfNgaN0T9r926HdWagWl1lJrZHJ06SIhNiNr8DO--Hg9KHOJ44B9xs3IzOvWGU31bk_cgzXxLBvOS82OfKLrlhD9nnbdKM2D6AoCDCztFFmWIVnDz2H6lYQGCgW5tJoQKAGlemGg027Rya9HLbXx7FG89yOdLbnvgaXHVfyPU9QG0kENdCpWuVo0qUnjfhhije5VmwpwF4GdDFdvHIMR30Xp6Nep_hYbA4QyBbMdTZaxQLWokZhIL2KugBfVo6I_1y1n5dJn_4KDE1pC3M-_kpOEeqpMGqBnABO5hV2FlvylDv8bXYV4opPw37bBBV1eNcVMQE5IjArPyv_q0HdH5ygiXvIPKBsoyQLldfA7-KeaMlHqTP22dRPRz4QijDrG0GbE6SYgn4k-HAR2CUt7RY1SEEkm7BruSaI78G_ViD0R9pCsU8ysuOTH8MLb8Ukda1DbLd2LjjEoDEmmXWFT8YN-MucITJ9DraWkRdkoLHcZHCMPkIVBeK1G-QnER6XTuLyaE-lT6alGwyb_NpLhghHt1xF3mByCOFA=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c0800005e1413f9_0%7C0a220b774c0b00004bb09d25_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EF45_3bCa1rkH2JW2NxmZl0h3RA-1Rp_hK4OpC9lbrMo0b7fjs98If2_oPbtM-SUyl8yWzY839EBWeQ4eqmhU9L4RFerR5lvz1JDgmc06OKUD-ZmGeAyaAicUUf10TrdFIOer09Kpr3Arqh7bHshwD4GSMPQrOGx1316M21W76majUPJ0PPX1NFsRHDunELqmXOozp7jIcWYa3l1WjHVAe0rCLBEPKmqI34VB5qhGeaH0FBE-BK3VZ9fQjal2bBO8wTOs0CxCFfNgaN0T9r926HdWagWl1lJrZHJ06SIhNiNr8DO--Hg9KHOJ44B9xs3IzOvWGU31bk_cgzXxLBvOS82OfKLrlhD9nnbdKM2D6AoCDCztFFmWIVnDz2H6lYQGCgW5tJoQKAGlemGg027Rya9HLbXx7FG89yOdLbnvgaXHVfyPU9QG0kENdCpWuVo0qUnjfhhije5VmwpwF4GdDFdvHIMR30Xp6Nep_hYbA4QyBbMdTZaxQLWokZhIL2KugBfVo6I_1y1n5dJn_4KDE1pC3M-_kpOEeqpMGqBnABO5hV2FlvylDv8bXYV4opPw37bBBV1eNcVMQE5IjArPyv_q0HdH5ygiXvIPKBsoyQLldfA7-KeaMlHqTP22dRPRz4QijDrG0GbE6SYgn4k-HAR2CUt7RY1SEEkm7BruSaI78G_ViD0R9pCsU8ysuOTH8MLb8Ukda1DbLd2LjjEoDEmmXWFT8YN-MucITJ9DraWkRdkoLHcZHCMPkIVBeK1G-QnER6XTuLyaE-lT6alGwyb_NpLhghHt1xF3mByCOFA=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-04-17T19:45:00.000Z", "utc_arrival": "2023-04-17T17:45:00.000Z", "local_departure": "2023-04-17T16:15:00.000Z", "utc_departure": "2023-04-17T14:15:00.000Z"}, {"id": "0b770a224c4400001cdf0063_0|0a220b774c47000069bc4867_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 794.033606, "distance": 1975.87, "duration": {"departure": 12600, "return": 11700, "total": 24300}, "price": 243733.1458, "conversion": {"EUR": 638.033996, "HUF": 243733.1458}, "fare": {"adults": 121866.57, "children": 125197.61, "infants": 125197.61}, "bags_price": {"1": 90.986, "2": 181.972}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 439, "hold_height": 149, "hold_length": 171, "hold_weight": 20, "hold_width": 119, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 6}, "airlines": ["W6"], "route": [{"id": "0b770a224c4400001cdf0063_0", "combination_id": "0b770a224c4400001cdf0063", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "HIREG", "fare_category": "M", "fare_classes": "H", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-16T19:45:00.000Z", "utc_arrival": "2023-06-16T17:45:00.000Z", "local_departure": "2023-06-16T16:15:00.000Z", "utc_departure": "2023-06-16T14:15:00.000Z"}, {"id": "0a220b774c47000069bc4867_0", "combination_id": "0a220b774c47000069bc4867", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-19T23:45:00.000Z", "utc_arrival": "2023-06-19T21:45:00.000Z", "local_departure": "2023-06-19T20:30:00.000Z", "utc_departure": "2023-06-19T18:30:00.000Z"}], "booking_token": "ExpN-sA_CKJuZ5Saso_XUGM9Kp5p81h22lWuCb6kIJQLXeZsRsXhLK8UzjBP7a9jYWUjo0sGCQtKIXKXIrB9hVNQVGsFurCg9SC6hk5Th-ZMZn4Hhvgbzvom1DZRQf1Ry2Nkf14wRPZgmFXwKfdU5VGdnVXPTpjxO5b-qjbSSNilpWLXEKWO9-eT6BZmQ-NR7b4TipZoA-6IqE4jc2jrNBppcrqHQfK-uqcyIhOOimCWUgNWjwGgpaSQln-zQ7_o5OqqGIs1cPqZ-KnIfqEZQ9CaVDWhusv1uJ08Gx5w3UPgMJDA5tCyTHx7lVnJ1HOLCArnvmQPDoJJnSOhDojZegSwRPYOJ9s4yfkUvf2vQytrKgLuRlhYgp-BVK_0YcO7HQFHjxsHsMiRDmZx_mUFAGU3JsaULDq7RY0NrWKGPNGLC892Y1wEOlrFTSEEjpSixicpp4svdvqGCccha5Xp2z-PN9zn82u7ijHrMJzUCbULEIB0vveOXAG0QoqWm2mh45Tgd2daa6l00ePqDEVs7PcA-wR1yRzEHzOLalOIPbOp7y3Ejsh3WsN_ZczqX2eG3QFUgc7WCIVuwKg4tJ8wb6X8-VBkEkZWjjKIIrJ5KmY3wiX7JEX3oOwq2TBtIGghKAx1XmRESYN6m_O4oUwkP_J0GAxrM1ElnHS72tuTayUjLAg6km91UBXBnwE7admDO-zE2EN2v4DtUiOq2ENYWGotIgU-bSLhMkEh4_PTxvptLw4pXtemBbLoccONan7Dg0tkzAKoQR2iSEXjBEfgTvkZEIe50VLqiqov1Je_bc2I=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c4400001cdf0063_0%7C0a220b774c47000069bc4867_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=ExpN-sA_CKJuZ5Saso_XUGM9Kp5p81h22lWuCb6kIJQLXeZsRsXhLK8UzjBP7a9jYWUjo0sGCQtKIXKXIrB9hVNQVGsFurCg9SC6hk5Th-ZMZn4Hhvgbzvom1DZRQf1Ry2Nkf14wRPZgmFXwKfdU5VGdnVXPTpjxO5b-qjbSSNilpWLXEKWO9-eT6BZmQ-NR7b4TipZoA-6IqE4jc2jrNBppcrqHQfK-uqcyIhOOimCWUgNWjwGgpaSQln-zQ7_o5OqqGIs1cPqZ-KnIfqEZQ9CaVDWhusv1uJ08Gx5w3UPgMJDA5tCyTHx7lVnJ1HOLCArnvmQPDoJJnSOhDojZegSwRPYOJ9s4yfkUvf2vQytrKgLuRlhYgp-BVK_0YcO7HQFHjxsHsMiRDmZx_mUFAGU3JsaULDq7RY0NrWKGPNGLC892Y1wEOlrFTSEEjpSixicpp4svdvqGCccha5Xp2z-PN9zn82u7ijHrMJzUCbULEIB0vveOXAG0QoqWm2mh45Tgd2daa6l00ePqDEVs7PcA-wR1yRzEHzOLalOIPbOp7y3Ejsh3WsN_ZczqX2eG3QFUgc7WCIVuwKg4tJ8wb6X8-VBkEkZWjjKIIrJ5KmY3wiX7JEX3oOwq2TBtIGghKAx1XmRESYN6m_O4oUwkP_J0GAxrM1ElnHS72tuTayUjLAg6km91UBXBnwE7admDO-zE2EN2v4DtUiOq2ENYWGotIgU-bSLhMkEh4_PTxvptLw4pXtemBbLoccONan7Dg0tkzAKoQR2iSEXjBEfgTvkZEIe50VLqiqov1Je_bc2I=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-16T19:45:00.000Z", "utc_arrival": "2023-06-16T17:45:00.000Z", "local_departure": "2023-06-16T16:15:00.000Z", "utc_departure": "2023-06-16T14:15:00.000Z"}, {"id": "0b770a224bf000009aab5dae_0|0a220b774bf3000020faa1b2_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 793.419023, "distance": 1975.87, "duration": {"departure": 12000, "return": 11700, "total": 23700}, "price": 244517.0526, "conversion": {"EUR": 640.086073, "HUF": 244517.0526}, "fare": {"adults": 122258.53, "children": 125596.53, "infants": 125596.53}, "bags_price": {"1": 86.618, "2": 173.25}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 439, "hold_height": 149, "hold_length": 171, "hold_weight": 20, "hold_width": 119, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 2}, "airlines": ["W6"], "route": [{"id": "0b770a224bf000009aab5dae_0", "combination_id": "0b770a224bf000009aab5dae", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "HREG", "fare_category": "M", "fare_classes": "H", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-03-24T19:40:00.000Z", "utc_arrival": "2023-03-24T18:40:00.000Z", "local_departure": "2023-03-24T16:20:00.000Z", "utc_departure": "2023-03-24T15:20:00.000Z"}, {"id": "0a220b774bf3000020faa1b2_0", "combination_id": "0a220b774bf3000020faa1b2", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IJREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-03-27T23:45:00.000Z", "utc_arrival": "2023-03-27T21:45:00.000Z", "local_departure": "2023-03-27T20:30:00.000Z", "utc_departure": "2023-03-27T18:30:00.000Z"}], "booking_token": "EbDLF148YqyBTD4CCllzuTBg0m4gBXa_5g_jWqd3gm1jiDvd9JgZBTae-NBmKssQI2oVXN-9WOavLV0PGo1Cet4QfmpXwohNpinxmmwzF8fRpcM9zbfLo7E_2_b313Ff5bCmsDFofe9dYMthgUqzPLTOSqMSeYXE63VC9WrNlWcfw7R2FZI-D2hginGbHnQEKXTuseQdXyAyXNbU9lwTHdgyPTUhGf-D6N82QAnpamJhCSM8vmfYqGB842SYrXneqe-S6ed8poAqPQ-pv3BFZUiTiX5UjoV7Dh5oFzX-hAjnZENrpz119fl7Rdy6c3kLbMoV82Dreg_SdSMs4DQZn8pMf-MnJYvBR-iQbfuTqajcDpsisIxFxTty5gx74UcQUxdmBVP5dTO3n4jC45nUwsZqQIa8RrVWRvRvsJravCvaNVN5CbV2jC2gk4cBSMjlz3g1ZrVfTvkO2lC-u7PgH0NoelxpgjvNtx0GMAEEb7aG8oI7UTc8KPczqMl7EE4MLUZRZ4TYATZaFyx2ZWa3pipyaWt-QTS6VOSHKGUrjgtPSVekFZPoF7rAH6ELSGKu4A2tqI2w4pyNypCamJWGnIUwHJO9OG1N0roXw3xRJpJgaMRQY94F-XqQy9WBIAov3eWT9S4k6qpdMnhJifQ5ytm4kitKpDOwDLvF9EML3O2HYWSnuS3lNvjhQUGQlw0GS7qdXeUUNKOpLXSTLXF04UZHkP2mZKX17Hy3HwJkW081ZQtAWOeLMuvREh5slcuAlXhz1h1O_B-NhFyEIk7nsUQWd5fUE50xsqaR0bzrA-naybZW0V21Gv13BaORYYDcs", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224bf000009aab5dae_0%7C0a220b774bf3000020faa1b2_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EbDLF148YqyBTD4CCllzuTBg0m4gBXa_5g_jWqd3gm1jiDvd9JgZBTae-NBmKssQI2oVXN-9WOavLV0PGo1Cet4QfmpXwohNpinxmmwzF8fRpcM9zbfLo7E_2_b313Ff5bCmsDFofe9dYMthgUqzPLTOSqMSeYXE63VC9WrNlWcfw7R2FZI-D2hginGbHnQEKXTuseQdXyAyXNbU9lwTHdgyPTUhGf-D6N82QAnpamJhCSM8vmfYqGB842SYrXneqe-S6ed8poAqPQ-pv3BFZUiTiX5UjoV7Dh5oFzX-hAjnZENrpz119fl7Rdy6c3kLbMoV82Dreg_SdSMs4DQZn8pMf-MnJYvBR-iQbfuTqajcDpsisIxFxTty5gx74UcQUxdmBVP5dTO3n4jC45nUwsZqQIa8RrVWRvRvsJravCvaNVN5CbV2jC2gk4cBSMjlz3g1ZrVfTvkO2lC-u7PgH0NoelxpgjvNtx0GMAEEb7aG8oI7UTc8KPczqMl7EE4MLUZRZ4TYATZaFyx2ZWa3pipyaWt-QTS6VOSHKGUrjgtPSVekFZPoF7rAH6ELSGKu4A2tqI2w4pyNypCamJWGnIUwHJO9OG1N0roXw3xRJpJgaMRQY94F-XqQy9WBIAov3eWT9S4k6qpdMnhJifQ5ytm4kitKpDOwDLvF9EML3O2HYWSnuS3lNvjhQUGQlw0GS7qdXeUUNKOpLXSTLXF04UZHkP2mZKX17Hy3HwJkW081ZQtAWOeLMuvREh5slcuAlXhz1h1O_B-NhFyEIk7nsUQWd5fUE50xsqaR0bzrA-naybZW0V21Gv13BaORYYDcs", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-03-24T19:40:00.000Z", "utc_arrival": "2023-03-24T18:40:00.000Z", "local_departure": "2023-03-24T16:20:00.000Z", "utc_departure": "2023-03-24T15:20:00.000Z"}, {"id": "0b770a224c144c18d9fe7d04_0|0b770a224c144c18d9fe7d04_1", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 790.896202, "distance": 1975.87, "duration": {"departure": 11700, "return": 11400, "total": 23100}, "price": 244572, "conversion": {"EUR": 640.229912, "HUF": 244572}, "fare": {"adults": 122286, "children": 122286, "infants": 122286}, "bags_price": {"1": 78.4, "2": 176.4}, "baglimit": {"hand_height": 40, "hand_length": 56, "hand_weight": 10, "hand_width": 25, "hold_dimensions_sum": 158, "hold_height": 52, "hold_length": 78, "hold_weight": 23, "hold_width": 28, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 3, "personal_item_width": 15}, "availability": {"seats": 3}, "airlines": ["IB"], "route": [{"id": "0b770a224c144c18d9fe7d04_0", "combination_id": "0b770a224c144c18d9fe7d04", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "IB", "flight_no": 3279, "operating_carrier": "IB", "operating_flight_no": "3279", "fare_basis": "ODNNANB4", "fare_category": "M", "fare_classes": "O", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-29T18:50:00.000Z", "utc_arrival": "2023-04-29T16:50:00.000Z", "local_departure": "2023-04-29T15:35:00.000Z", "utc_departure": "2023-04-29T13:35:00.000Z"}, {"id": "0b770a224c144c18d9fe7d04_1", "combination_id": "0b770a224c144c18d9fe7d04", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "IB", "flight_no": 3278, "operating_carrier": "IB", "operating_flight_no": "3278", "fare_basis": "VDNNANB4", "fare_category": "M", "fare_classes": "V", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-03T14:55:00.000Z", "utc_arrival": "2023-05-03T12:55:00.000Z", "local_departure": "2023-05-03T11:45:00.000Z", "utc_departure": "2023-05-03T09:45:00.000Z"}], "booking_token": "E4ev5_pIscS9uqfH9eTgZEjSWjCPLxr21Lu5azSkf9cMP-_XeJ_N4KatGe7sU8Vbqh6uM22zmpuJpNmr0rhEIdZ5t4FuTA__wNOuRDXs3DITKJViRMQaAbh97rPAsTDW03SUYXb14RLqW84eaH1THIYoypWro3iAN-seSGwYqbCW5SbJmfmxyL0Suh6f5MQD8QFi174VYlR0ZlNr2iweeVOTzX1YDeHXBJt1wfdUOObVlaNIdMyo8RHxgHfXJK5dZPnjbd9tBTloPBfyS5y0AqNvYMOvfDbSOYVg8ukCgOji5LJeG1DGRVlwONH7iXCk8I1hdh9-UC81eFblTq0fAYdTIh7yhO0rt04XCBjHaYFMO-igUlinpVBrI3mkFhynCt04XDFhyxYPhlnTia7JOR3TqUlNiCqho7Oi43WOk1hddA_MneqMl5tVSOTS79REiwCvpUS8pVe0TyJvHfiPpCEC-6w94_GSlJlRgcl42kjIVzaUfSCr5wjwSTj-cmR_QyPqsDGS3P8ddeS1dGXrhloZnu2u1DtJOKdSYrXUZGs6bfnmSBIXeLBHbXGyKlbggyYyX_WJ4s34eX5EAZfcH7K-KEgvox0IrgnwxvHAZWV7Lw2S1W6ig8zHU1cExDf9lG2Xa-kOTSo9BOwO6oyP-cJrcmnljjrNN1OQ1YAn5cIzkGW5SYNQKNXU0eW7vzxe9HiNFh6FINPCGR8R2UPT3ahhnKb6Fhch8MV3OKkLQEq1dlGZmAqi6LvC6O5AHQp2d", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c144c18d9fe7d04_0%7C0b770a224c144c18d9fe7d04_1&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=E4ev5_pIscS9uqfH9eTgZEjSWjCPLxr21Lu5azSkf9cMP-_XeJ_N4KatGe7sU8Vbqh6uM22zmpuJpNmr0rhEIdZ5t4FuTA__wNOuRDXs3DITKJViRMQaAbh97rPAsTDW03SUYXb14RLqW84eaH1THIYoypWro3iAN-seSGwYqbCW5SbJmfmxyL0Suh6f5MQD8QFi174VYlR0ZlNr2iweeVOTzX1YDeHXBJt1wfdUOObVlaNIdMyo8RHxgHfXJK5dZPnjbd9tBTloPBfyS5y0AqNvYMOvfDbSOYVg8ukCgOji5LJeG1DGRVlwONH7iXCk8I1hdh9-UC81eFblTq0fAYdTIh7yhO0rt04XCBjHaYFMO-igUlinpVBrI3mkFhynCt04XDFhyxYPhlnTia7JOR3TqUlNiCqho7Oi43WOk1hddA_MneqMl5tVSOTS79REiwCvpUS8pVe0TyJvHfiPpCEC-6w94_GSlJlRgcl42kjIVzaUfSCr5wjwSTj-cmR_QyPqsDGS3P8ddeS1dGXrhloZnu2u1DtJOKdSYrXUZGs6bfnmSBIXeLBHbXGyKlbggyYyX_WJ4s34eX5EAZfcH7K-KEgvox0IrgnwxvHAZWV7Lw2S1W6ig8zHU1cExDf9lG2Xa-kOTSo9BOwO6oyP-cJrcmnljjrNN1OQ1YAn5cIzkGW5SYNQKNXU0eW7vzxe9HiNFh6FINPCGR8R2UPT3ahhnKb6Fhch8MV3OKkLQEq1dlGZmAqi6LvC6O5AHQp2d", "facilitated_booking_available": true, "pnr_count": 1, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-04-29T18:50:00.000Z", "utc_arrival": "2023-04-29T16:50:00.000Z", "local_departure": "2023-04-29T15:35:00.000Z", "utc_departure": "2023-04-29T13:35:00.000Z"}, {"id": "0b770a224c4000007558117a_0|0a220b774c44000078e26f99_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 795.018061, "distance": 1975.87, "duration": {"departure": 12600, "return": 11400, "total": 24000}, "price": 244618.5548, "conversion": {"EUR": 640.351781, "HUF": 244618.5548}, "fare": {"adults": 122309.28, "children": 122309.28, "infants": 122309.28}, "bags_price": {"1": 98.7, "2": 197.414}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 3}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224c4000007558117a_0", "combination_id": "0b770a224c4000007558117a", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "HREG", "fare_category": "M", "fare_classes": "H", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-12T19:45:00.000Z", "utc_arrival": "2023-06-12T17:45:00.000Z", "local_departure": "2023-06-12T16:15:00.000Z", "utc_departure": "2023-06-12T14:15:00.000Z"}, {"id": "0a220b774c44000078e26f99_0", "combination_id": "0a220b774c44000078e26f99", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-16T18:00:00.000Z", "utc_arrival": "2023-06-16T16:00:00.000Z", "local_departure": "2023-06-16T14:50:00.000Z", "utc_departure": "2023-06-16T12:50:00.000Z"}], "booking_token": "Epsa_xNZcSbQOem9JqWeY_8qM-GSJ5ApQAFZIRrkFxwhSe3sBAx69le9S8RuBxp9iZUmENmRC4K6HT21MfIJktHUUt_aSbfPvxiJTvUgmmTqm2GaD-erO8qQh_0AxLAdIwwQdYZfOvz8dNuMWN6-vtNV9DUJJCst2EGA5rLnIovyAKHp8i4_-2B9MCqB1aMKRfSJ3P_Qr-KXq3gssE-cndhXfFN-LHHGWHkXftQaA-8NmqrEnu-AY-JwjJyxq6bQTaK2GIIURCtovGpFCAgDuRK8llUXqtfKhxh1eeKbZYRd1qzMsuIz87Vwwt8xVGzfgrxA6e3Jk3mNoyrH8uKOWPZpkVjBpO9mzGMh_gA_7MoI_ZRnasO1W2uQaDnYAN7aYiUyAZ1dzvTX2ll3ZZ0CxId6wDpnxoVSM2py85h46eatSJuZcoLZn3hDiZKGKRVl_RiDCsFIq0sMh1lJRjoTTYaYeyjnxWbG_2hayGrnHQaMfq6tHJpQaNPfkuZScj06exyKPkNFfSV7cYyMenbji_PjyaAtfy_4ojOI-R63Woc2hLgAAa-U12mHHiozM89Cl1oTP1CFp7Y8NKECbrcav3xEx_EB2jhZTMtNFbi_YRSZIAUJlVEy2ZQ9FjS3qgULg2_47lrExHwEiyajrGWFjEkgEhlOtmXqB34kOmqBSf6HCBRdRREVAusDYYIoYAm3qHzCkqJu4j-11H2K9BBfPJLwtpmCWbe5skRLccKlx5cuSsQpZiW3dBSpj1ubA4Pg0benztBXBWCZwktU_Cy3O0g==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c4000007558117a_0%7C0a220b774c44000078e26f99_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=Epsa_xNZcSbQOem9JqWeY_8qM-GSJ5ApQAFZIRrkFxwhSe3sBAx69le9S8RuBxp9iZUmENmRC4K6HT21MfIJktHUUt_aSbfPvxiJTvUgmmTqm2GaD-erO8qQh_0AxLAdIwwQdYZfOvz8dNuMWN6-vtNV9DUJJCst2EGA5rLnIovyAKHp8i4_-2B9MCqB1aMKRfSJ3P_Qr-KXq3gssE-cndhXfFN-LHHGWHkXftQaA-8NmqrEnu-AY-JwjJyxq6bQTaK2GIIURCtovGpFCAgDuRK8llUXqtfKhxh1eeKbZYRd1qzMsuIz87Vwwt8xVGzfgrxA6e3Jk3mNoyrH8uKOWPZpkVjBpO9mzGMh_gA_7MoI_ZRnasO1W2uQaDnYAN7aYiUyAZ1dzvTX2ll3ZZ0CxId6wDpnxoVSM2py85h46eatSJuZcoLZn3hDiZKGKRVl_RiDCsFIq0sMh1lJRjoTTYaYeyjnxWbG_2hayGrnHQaMfq6tHJpQaNPfkuZScj06exyKPkNFfSV7cYyMenbji_PjyaAtfy_4ojOI-R63Woc2hLgAAa-U12mHHiozM89Cl1oTP1CFp7Y8NKECbrcav3xEx_EB2jhZTMtNFbi_YRSZIAUJlVEy2ZQ9FjS3qgULg2_47lrExHwEiyajrGWFjEkgEhlOtmXqB34kOmqBSf6HCBRdRREVAusDYYIoYAm3qHzCkqJu4j-11H2K9BBfPJLwtpmCWbe5skRLccKlx5cuSsQpZiW3dBSpj1ubA4Pg0benztBXBWCZwktU_Cy3O0g==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-12T19:45:00.000Z", "utc_arrival": "2023-06-12T17:45:00.000Z", "local_departure": "2023-06-12T16:15:00.000Z", "utc_departure": "2023-06-12T14:15:00.000Z"}, {"id": "0b770a224c050000101ee0e9_0|0a220b774c090000137a3e18_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 795.590224, "distance": 1975.87, "duration": {"departure": 12600, "return": 11400, "total": 24000}, "price": 244837.1248, "conversion": {"EUR": 640.923944, "HUF": 244837.1248}, "fare": {"adults": 122418.56, "children": 122418.56, "infants": 122418.56}, "bags_price": {"1": 113.652, "2": 227.304}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 3}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224c050000101ee0e9_0", "combination_id": "0b770a224c050000101ee0e9", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-14T19:45:00.000Z", "utc_arrival": "2023-04-14T17:45:00.000Z", "local_departure": "2023-04-14T16:15:00.000Z", "utc_departure": "2023-04-14T14:15:00.000Z"}, {"id": "0a220b774c090000137a3e18_0", "combination_id": "0a220b774c090000137a3e18", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-18T14:05:00.000Z", "utc_arrival": "2023-04-18T12:05:00.000Z", "local_departure": "2023-04-18T10:55:00.000Z", "utc_departure": "2023-04-18T08:55:00.000Z"}], "booking_token": "Ej3V9iND3CC7gWcqDMAmN7PCxK3zOcp2dTZyY7Cuj_v3gsA-B624z9JbOYBcIP4pa9FWi3_X6aOOZlHi1wgvjuJzrEriSOJO-diJ_igQdz6FY9v5WDklC0o_zPhMt2ENSUFF4e2hpU5uQiOQqEKOWIiRMERlFOjNRlBdD51sHBsIw0SkZ0b3B4fLv_4KxpE32o_G_eag7WLesNYcMdpw9AVvta1uG3nBjR7RMCBIfpfYoJsyMUv9RSJt69eG7K6mLEtKY8JjdbV22YWB8sDkTvKGiEStKBa86-HdEDogd5NlZSVhwt1h7RyvUuifugy7lTlAz1pojNQBBTXGFQxKTayMraOFMN6QGu3Ueg9VYouNeJGMNg79s9Vk1nEO8BepNR1dWdp5eJHxf2w9mLnDq05MszoeBOJsuYOpiLGIypjSgHE1paW_xOM17FIi096AV8kP4_L_AZb6Pj8rM4mI1-8zZc3MPn6recPSx3jXsJ-9_ZPQvUJw5OWlc_q2EHX-jr7KyUQMlmGKb4XfAyq5o-FfUA11GTbzO5KhJyeE0KDAVHjwuqit0huHmZS0TC75KwAsm6qoknrdjPqRDB9519-vOW1F48Sw3G1FZO8TGagczkpvHoKefIA_6DdRH5mZ325fvFv5EkUxZHAoalQU6d1eVQmLso7406sOahN87HL9p89zndr-oT-_wjdOAfgSe37rVIXnLOY1cGvUXUbPmmWat8K6kjz17ReFmp2eW2kFh0Yrf7Rdy-3UpeR5hRGD2-f2J_OG7O6k_BQRrJaFmyg==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c050000101ee0e9_0%7C0a220b774c090000137a3e18_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=Ej3V9iND3CC7gWcqDMAmN7PCxK3zOcp2dTZyY7Cuj_v3gsA-B624z9JbOYBcIP4pa9FWi3_X6aOOZlHi1wgvjuJzrEriSOJO-diJ_igQdz6FY9v5WDklC0o_zPhMt2ENSUFF4e2hpU5uQiOQqEKOWIiRMERlFOjNRlBdD51sHBsIw0SkZ0b3B4fLv_4KxpE32o_G_eag7WLesNYcMdpw9AVvta1uG3nBjR7RMCBIfpfYoJsyMUv9RSJt69eG7K6mLEtKY8JjdbV22YWB8sDkTvKGiEStKBa86-HdEDogd5NlZSVhwt1h7RyvUuifugy7lTlAz1pojNQBBTXGFQxKTayMraOFMN6QGu3Ueg9VYouNeJGMNg79s9Vk1nEO8BepNR1dWdp5eJHxf2w9mLnDq05MszoeBOJsuYOpiLGIypjSgHE1paW_xOM17FIi096AV8kP4_L_AZb6Pj8rM4mI1-8zZc3MPn6recPSx3jXsJ-9_ZPQvUJw5OWlc_q2EHX-jr7KyUQMlmGKb4XfAyq5o-FfUA11GTbzO5KhJyeE0KDAVHjwuqit0huHmZS0TC75KwAsm6qoknrdjPqRDB9519-vOW1F48Sw3G1FZO8TGagczkpvHoKefIA_6DdRH5mZ325fvFv5EkUxZHAoalQU6d1eVQmLso7406sOahN87HL9p89zndr-oT-_wjdOAfgSe37rVIXnLOY1cGvUXUbPmmWat8K6kjz17ReFmp2eW2kFh0Yrf7Rdy-3UpeR5hRGD2-f2J_OG7O6k_BQRrJaFmyg==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-04-14T19:45:00.000Z", "utc_arrival": "2023-04-14T17:45:00.000Z", "local_departure": "2023-04-14T16:15:00.000Z", "utc_departure": "2023-04-14T14:15:00.000Z"}, {"id": "0b770a224c130000597a9e5b_0|0a220b774c1600007449e031_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 795.745642, "distance": 1975.87, "duration": {"departure": 12600, "return": 11400, "total": 24000}, "price": 244896.4955, "conversion": {"EUR": 641.079362, "HUF": 244896.4955}, "fare": {"adults": 122448.25, "children": 122448.25, "infants": 122448.25}, "bags_price": {"1": 106.862, "2": 213.738}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 5}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224c130000597a9e5b_0", "combination_id": "0b770a224c130000597a9e5b", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "KREG", "fare_category": "M", "fare_classes": "K", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-28T19:45:00.000Z", "utc_arrival": "2023-04-28T17:45:00.000Z", "local_departure": "2023-04-28T16:15:00.000Z", "utc_departure": "2023-04-28T14:15:00.000Z"}, {"id": "0a220b774c1600007449e031_0", "combination_id": "0a220b774c1600007449e031", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-01T10:15:00.000Z", "utc_arrival": "2023-05-01T08:15:00.000Z", "local_departure": "2023-05-01T07:05:00.000Z", "utc_departure": "2023-05-01T05:05:00.000Z"}], "booking_token": "EZya6gUnjSTLE0-mAmW1aDFjjuvQSRUay8qt5nSWCA0HY6yApmDacFoiVqjNoWi7VNILOpeqCPsqXF2AjyFFV7gog-Wd1qeVFuJtRSYC8wkSlpCNNcabR_i3VFfNZyEtMzpTJgnZqAsD8yAqPNYfGPe_notZMM-8SrZ1xVLsoQibLRZG9hR1JXR4c6YXga8CRuK4WS1zLtNDGrKeggOc8TWg3JFng7lZoBmCo_4MVUDHsN-w7vyG7Auxv-ZaLa-i72MUAvlMAgDNwFfm-vd5lQGQSYzUhdXrOMxdk-ytkMpqGRWa2hyB4hkmW1OOMlNtyPvGKOGux0r8CxK-2HzB8SXxJFx1XbzBXtb2s2D6pFI2mMqFba1yZXjU3LbHhyZTCIAAw6UsMtmIvVkm4zbeUdQVXmlAWTJ4YDql89M_xm2hFjLBncMssVZ67dagO-setvAPoM1T5UKShAQoQWbtIz4MaO6LUr0iwBpg7UpXk8QbmNvtKs3uBf9jhLeKV5TVAYYQHw6V6uINuB0dGShlg1d1U6oDriq0N-eawA2j5EkBXyzKlPR8zLn2FQ1YsmyrEsew3zmna9Xmof3x3bzstrsJ8G6wPrz0e2AKfKQIcXxpV4sloP163M3E67wTnM1TKc3NhFqkCmMwiPygnC9jkgyq-odTi_cuSrYxQwp7xPMP_-inEJcernzDpVKEyEKtA4AYwdyQX-9Vlsju4anmxHS3POEFDO7mvg-c5sZzStfa1w4zUEfs2L9sHvFLNntkEIW_QTO5UENgjpCoMjIpGreA5023f0aNE4lV2jdSoT0M=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c130000597a9e5b_0%7C0a220b774c1600007449e031_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EZya6gUnjSTLE0-mAmW1aDFjjuvQSRUay8qt5nSWCA0HY6yApmDacFoiVqjNoWi7VNILOpeqCPsqXF2AjyFFV7gog-Wd1qeVFuJtRSYC8wkSlpCNNcabR_i3VFfNZyEtMzpTJgnZqAsD8yAqPNYfGPe_notZMM-8SrZ1xVLsoQibLRZG9hR1JXR4c6YXga8CRuK4WS1zLtNDGrKeggOc8TWg3JFng7lZoBmCo_4MVUDHsN-w7vyG7Auxv-ZaLa-i72MUAvlMAgDNwFfm-vd5lQGQSYzUhdXrOMxdk-ytkMpqGRWa2hyB4hkmW1OOMlNtyPvGKOGux0r8CxK-2HzB8SXxJFx1XbzBXtb2s2D6pFI2mMqFba1yZXjU3LbHhyZTCIAAw6UsMtmIvVkm4zbeUdQVXmlAWTJ4YDql89M_xm2hFjLBncMssVZ67dagO-setvAPoM1T5UKShAQoQWbtIz4MaO6LUr0iwBpg7UpXk8QbmNvtKs3uBf9jhLeKV5TVAYYQHw6V6uINuB0dGShlg1d1U6oDriq0N-eawA2j5EkBXyzKlPR8zLn2FQ1YsmyrEsew3zmna9Xmof3x3bzstrsJ8G6wPrz0e2AKfKQIcXxpV4sloP163M3E67wTnM1TKc3NhFqkCmMwiPygnC9jkgyq-odTi_cuSrYxQwp7xPMP_-inEJcernzDpVKEyEKtA4AYwdyQX-9Vlsju4anmxHS3POEFDO7mvg-c5sZzStfa1w4zUEfs2L9sHvFLNntkEIW_QTO5UENgjpCoMjIpGreA5023f0aNE4lV2jdSoT0M=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-04-28T19:45:00.000Z", "utc_arrival": "2023-04-28T17:45:00.000Z", "local_departure": "2023-04-28T16:15:00.000Z", "utc_departure": "2023-04-28T14:15:00.000Z"}, {"id": "0b770a224c440000087d9250_0|0a220b774c470000d863fde0_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 793.27359, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 244970.837, "conversion": {"EUR": 641.27397, "HUF": 244970.837}, "fare": {"adults": 122485.42, "children": 122485.42, "infants": 122485.42}, "bags_price": {"1": 80.682, "2": 171.15}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 158, "hold_height": 52, "hold_length": 78, "hold_weight": 20, "hold_width": 28, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 3, "personal_item_width": 15}, "availability": {"seats": 3}, "airlines": ["FR", "IB"], "route": [{"id": "0b770a224c440000087d9250_0", "combination_id": "0b770a224c440000087d9250", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-16T21:45:00.000Z", "utc_arrival": "2023-06-16T19:45:00.000Z", "local_departure": "2023-06-16T18:25:00.000Z", "utc_departure": "2023-06-16T16:25:00.000Z"}, {"id": "0a220b774c470000d863fde0_0", "combination_id": "0a220b774c470000d863fde0", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "IB", "flight_no": 3278, "operating_carrier": "IB", "operating_flight_no": "3278", "fare_basis": "SWNNAOB4", "fare_category": "M", "fare_classes": "S", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-19T14:55:00.000Z", "utc_arrival": "2023-06-19T12:55:00.000Z", "local_departure": "2023-06-19T11:45:00.000Z", "utc_departure": "2023-06-19T09:45:00.000Z"}], "booking_token": "EE679aqmu33gm0TWPTpCW0neysQWDW94GGA-iswHtvq840cSZXW4zfs5lQgbtOYUOQQhWBMRypt0feoSohUPjOFbr-UEmLuGqyVb-lhwywoi-7e0oqWMmi3yUTNCRpJA-i1J6V5Lq_3o1QBfiIK69dektICHA3cSWwggMgnotV4-z-Kon5N_pUhWx8WSomPIITrtjdqDx0Pcnptk9WX0e1VTBHEEjN_9zTXXIoXE1-vlOkhj_D_pj0afV-dz1xuS_fzX6ZdQ-3BR5LeiakrhO3I3u5KGnnvoZpAfDunvzGe4ijhtSEYeMSHtgPj6rra2KyNdtrsgtN-4SzzzhI9rhCcS-KeC3lCfk9T13SauDk84fV_JSVvqpx_GHDDdisVFnmCMptQf5Cj0vPC6s56gmhr27o5N_FzsxSEy-J26kKbZ7pUXYSt1u8MxeTtbmFc_lgst9SenlNGF5dmxN-Ap3NfmuS84JyhOjRlUUitJy4BnR-qQP1RlBRVO_0kq4RXLmaoRpBTLXRJ0f7EXdAvoRagPtLAKuTkwifQo-bliRiEK2oUs1Yo1Ns6ET6Y3bM_moICrnvlB5NJbGCuJtbTETlvXi_z8hy4byIONfh1y19lhSFJY9rXMfln48mpGht3b7n3phUN4hkvf4My3fATVnL3L423MBV6CN5QdO4Z-WH-69NMOlq76yqeaS1kNHBjAseikvzPSADDxkMbYPIp8dLVJgyeyws1hnKqf8xV4dlLXuGKAA1lak8vrROcauV6qHxUkqeGjLzAEaQ5Q5Jm2cOudIvhO27rmAXV9vOhuWPOE=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c440000087d9250_0%7C0a220b774c470000d863fde0_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EE679aqmu33gm0TWPTpCW0neysQWDW94GGA-iswHtvq840cSZXW4zfs5lQgbtOYUOQQhWBMRypt0feoSohUPjOFbr-UEmLuGqyVb-lhwywoi-7e0oqWMmi3yUTNCRpJA-i1J6V5Lq_3o1QBfiIK69dektICHA3cSWwggMgnotV4-z-Kon5N_pUhWx8WSomPIITrtjdqDx0Pcnptk9WX0e1VTBHEEjN_9zTXXIoXE1-vlOkhj_D_pj0afV-dz1xuS_fzX6ZdQ-3BR5LeiakrhO3I3u5KGnnvoZpAfDunvzGe4ijhtSEYeMSHtgPj6rra2KyNdtrsgtN-4SzzzhI9rhCcS-KeC3lCfk9T13SauDk84fV_JSVvqpx_GHDDdisVFnmCMptQf5Cj0vPC6s56gmhr27o5N_FzsxSEy-J26kKbZ7pUXYSt1u8MxeTtbmFc_lgst9SenlNGF5dmxN-Ap3NfmuS84JyhOjRlUUitJy4BnR-qQP1RlBRVO_0kq4RXLmaoRpBTLXRJ0f7EXdAvoRagPtLAKuTkwifQo-bliRiEK2oUs1Yo1Ns6ET6Y3bM_moICrnvlB5NJbGCuJtbTETlvXi_z8hy4byIONfh1y19lhSFJY9rXMfln48mpGht3b7n3phUN4hkvf4My3fATVnL3L423MBV6CN5QdO4Z-WH-69NMOlq76yqeaS1kNHBjAseikvzPSADDxkMbYPIp8dLVJgyeyws1hnKqf8xV4dlLXuGKAA1lak8vrROcauV6qHxUkqeGjLzAEaQ5Q5Jm2cOudIvhO27rmAXV9vOhuWPOE=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-16T21:45:00.000Z", "utc_arrival": "2023-06-16T19:45:00.000Z", "local_departure": "2023-06-16T18:25:00.000Z", "utc_departure": "2023-06-16T16:25:00.000Z"}, {"id": "0b770a224bf30000be6b3d57_0|0a220b774bf600003991cd2d_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 798.770068, "distance": 1975.87, "duration": {"departure": 12600, "return": 11700, "total": 24300}, "price": 245542.5052, "conversion": {"EUR": 642.770458, "HUF": 245542.5052}, "fare": {"adults": 122771.25, "children": 122771.25, "infants": 122771.25}, "bags_price": {"1": 93.422, "2": 186.844}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 439, "hold_height": 149, "hold_length": 171, "hold_weight": 20, "hold_width": 119, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 3}, "airlines": ["W6"], "route": [{"id": "0b770a224bf30000be6b3d57_0", "combination_id": "0b770a224bf30000be6b3d57", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IJREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-03-27T19:45:00.000Z", "utc_arrival": "2023-03-27T17:45:00.000Z", "local_departure": "2023-03-27T16:15:00.000Z", "utc_departure": "2023-03-27T14:15:00.000Z"}, {"id": "0a220b774bf600003991cd2d_0", "combination_id": "0a220b774bf600003991cd2d", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "GHREG", "fare_category": "M", "fare_classes": "G", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-03-31T01:15:00.000Z", "utc_arrival": "2023-03-30T23:15:00.000Z", "local_departure": "2023-03-30T22:00:00.000Z", "utc_departure": "2023-03-30T20:00:00.000Z"}], "booking_token": "EdPMXil77CsLI7Ec-yj0hYloaVkkJ1VV4ljrJEg2q5yDydZPXQTIC1liGlD1orn8W_Lf1kqW3c1WjJHtvBJbabwterPnlCQxZ94EXAi-pMBruliPAqZbjxsJBaVUy3H_pUItqTfyNUZzfdTAICDk4vta2xOSM76_VDCKGNjb03yFse-bodVGrSB0wGsuliCWmUC54i5JliSA-vW7dWRMSn-TVSqvn61gLR70nlZAXmHhu4EDXHik3YgqA2TSf01jsqvcW8w3IyLKL1ZW59hlkPCV0ikTcCiG9w5_b5jLbyLaPZwT9QXJ0DdXX0WybL3Q6SepdgqYYPJfOnaahCtXkYmUMepYsAK41YcAg8obK284dneX9Nv3kv1YLz5u3FLguve3ejBQUYqXftfLwIylhj_YPPWfrF200ixamdHTXDgfBEGt41wWPIxYLhjS9XdYlZIOqqt4aeMzdZ1ijbr_JZ3LE7hCUAKiugnnhHXGbOMSlGXiGI8Zl7Y7JzwaU0TvFr8eVTR0yoSBYt6wRwvdCBrFXnbBAGMaV2IwNiSKQfcQAtutX1V5MDU5iPuOPdA2cQGg2ZwJ6moBfYCiQna0AuKFXjdzB7xL_okSYwphCpINcwcTHbHfwkQ695nYzJmTQGFR3pTJU8EjQxDk_naPsAJ-JRc52uDUt9ggp-fPHihJxZAUCIS27tyMKFi8mS169zMdknhS5_BJNe1XXeYhEia5ZixSpUIFKyJ4tIO90qHfc3I9fTi5lUTf7-43PteccAc2tHjnuyTGzjG3RI-nJ45EllweQWKnbBXDweWKlKTI=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224bf30000be6b3d57_0%7C0a220b774bf600003991cd2d_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EdPMXil77CsLI7Ec-yj0hYloaVkkJ1VV4ljrJEg2q5yDydZPXQTIC1liGlD1orn8W_Lf1kqW3c1WjJHtvBJbabwterPnlCQxZ94EXAi-pMBruliPAqZbjxsJBaVUy3H_pUItqTfyNUZzfdTAICDk4vta2xOSM76_VDCKGNjb03yFse-bodVGrSB0wGsuliCWmUC54i5JliSA-vW7dWRMSn-TVSqvn61gLR70nlZAXmHhu4EDXHik3YgqA2TSf01jsqvcW8w3IyLKL1ZW59hlkPCV0ikTcCiG9w5_b5jLbyLaPZwT9QXJ0DdXX0WybL3Q6SepdgqYYPJfOnaahCtXkYmUMepYsAK41YcAg8obK284dneX9Nv3kv1YLz5u3FLguve3ejBQUYqXftfLwIylhj_YPPWfrF200ixamdHTXDgfBEGt41wWPIxYLhjS9XdYlZIOqqt4aeMzdZ1ijbr_JZ3LE7hCUAKiugnnhHXGbOMSlGXiGI8Zl7Y7JzwaU0TvFr8eVTR0yoSBYt6wRwvdCBrFXnbBAGMaV2IwNiSKQfcQAtutX1V5MDU5iPuOPdA2cQGg2ZwJ6moBfYCiQna0AuKFXjdzB7xL_okSYwphCpINcwcTHbHfwkQ695nYzJmTQGFR3pTJU8EjQxDk_naPsAJ-JRc52uDUt9ggp-fPHihJxZAUCIS27tyMKFi8mS169zMdknhS5_BJNe1XXeYhEia5ZixSpUIFKyJ4tIO90qHfc3I9fTi5lUTf7-43PteccAc2tHjnuyTGzjG3RI-nJ45EllweQWKnbBXDweWKlKTI=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-03-27T19:45:00.000Z", "utc_arrival": "2023-03-27T17:45:00.000Z", "local_departure": "2023-03-27T16:15:00.000Z", "utc_departure": "2023-03-27T14:15:00.000Z"}, {"id": "0b770a224c0c00004f039f60_0|0a220b774c0f0000a1c65665_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 795.115979, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 245674.6416, "conversion": {"EUR": 643.116359, "HUF": 245674.6416}, "fare": {"adults": 122837.32, "children": 122837.32, "infants": 122837.32}, "bags_price": {"1": 81.396, "2": 162.764}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 5}, "airlines": ["FR"], "route": [{"id": "0b770a224c0c00004f039f60_0", "combination_id": "0b770a224c0c00004f039f60", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-21T21:45:00.000Z", "utc_arrival": "2023-04-21T19:45:00.000Z", "local_departure": "2023-04-21T18:25:00.000Z", "utc_departure": "2023-04-21T16:25:00.000Z"}, {"id": "0a220b774c0f0000a1c65665_0", "combination_id": "0a220b774c0f0000a1c65665", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-24T10:15:00.000Z", "utc_arrival": "2023-04-24T08:15:00.000Z", "local_departure": "2023-04-24T07:05:00.000Z", "utc_departure": "2023-04-24T05:05:00.000Z"}], "booking_token": "EeOZz5O0TWVr5v8-6ciLJFW0ZCHDOX8Xr97c8aA34R6jx99qxhObN5yIUqTad-6TPgyP_SwCesiOxgURLIaMQbrEvQcblu_nKylVrb1OCWK9_zlsfvJYEfhwnITcRVKs5P4n4BryQEOkJscKgGa4kXK14DpP5-aUBx0vG6XgbA5LDHiDxK02LGkulxSVYKj0cT7MF7jCNsabAexMvX2oLvwoRlGb4JLOPti8z3fYSMNt3YbaVY-GXDu7n8jSIvWkIINI5RGxKmDHswl0q1CsCp3CV_-SCieixuFzFxhmq6SZCsN9_cpxXJ24ZBUdPZS6bkNa0QFnTBlDB9WobkwHrVTxoiZF5cnWVXSWiU-pWg_xpiSFcBsW5z8F-meX5EGlu4j-uOkIavDNbfs8JvPm4j9YMiI96cGm8208LOqnRydEr49xffDbzPCSrfx0soKK31sVWSzbabXPvAaQpDEI3x-qvv4yWKflqvZ9J-KYEHAENqQdTHpZZtn3O8oij-2zT9cccmP2dcx9LhrlsyoMVdA9UOhFO_NDS7R5fvz1WJ90z5hcdXHFJPf-qsEHmpzrMVsskvvyhwVY-hY72J3JBAr0w20cyxFPZeZuZKy0U5JmMEIDbv6C-bSEJzmlVSTaB1xJZhvWHSJh2qgyUdT3ppmC5-4VzHcNjO0Yfe0adoh4mQmPnpbAunow4e9AxjFEt9rXMY44RekzbXSlRJS03-PfBUye5qdJUg9U6SZiGrFN4bP2_a0k3KbpEjIwUQE7qT9viDLDHYFW8YIFegm02zO22bz1N8S_URdPFX7cveQ8=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c0c00004f039f60_0%7C0a220b774c0f0000a1c65665_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EeOZz5O0TWVr5v8-6ciLJFW0ZCHDOX8Xr97c8aA34R6jx99qxhObN5yIUqTad-6TPgyP_SwCesiOxgURLIaMQbrEvQcblu_nKylVrb1OCWK9_zlsfvJYEfhwnITcRVKs5P4n4BryQEOkJscKgGa4kXK14DpP5-aUBx0vG6XgbA5LDHiDxK02LGkulxSVYKj0cT7MF7jCNsabAexMvX2oLvwoRlGb4JLOPti8z3fYSMNt3YbaVY-GXDu7n8jSIvWkIINI5RGxKmDHswl0q1CsCp3CV_-SCieixuFzFxhmq6SZCsN9_cpxXJ24ZBUdPZS6bkNa0QFnTBlDB9WobkwHrVTxoiZF5cnWVXSWiU-pWg_xpiSFcBsW5z8F-meX5EGlu4j-uOkIavDNbfs8JvPm4j9YMiI96cGm8208LOqnRydEr49xffDbzPCSrfx0soKK31sVWSzbabXPvAaQpDEI3x-qvv4yWKflqvZ9J-KYEHAENqQdTHpZZtn3O8oij-2zT9cccmP2dcx9LhrlsyoMVdA9UOhFO_NDS7R5fvz1WJ90z5hcdXHFJPf-qsEHmpzrMVsskvvyhwVY-hY72J3JBAr0w20cyxFPZeZuZKy0U5JmMEIDbv6C-bSEJzmlVSTaB1xJZhvWHSJh2qgyUdT3ppmC5-4VzHcNjO0Yfe0adoh4mQmPnpbAunow4e9AxjFEt9rXMY44RekzbXSlRJS03-PfBUye5qdJUg9U6SZiGrFN4bP2_a0k3KbpEjIwUQE7qT9viDLDHYFW8YIFegm02zO22bz1N8S_URdPFX7cveQ8=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-04-21T21:45:00.000Z", "utc_arrival": "2023-04-21T19:45:00.000Z", "local_departure": "2023-04-21T18:25:00.000Z", "utc_departure": "2023-04-21T16:25:00.000Z"}, {"id": "0b770a224c37000093465fe3_0|0a220b774c3a0000fea059a3_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 796.358208, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 246149.1812, "conversion": {"EUR": 644.358588, "HUF": 246149.1812}, "fare": {"adults": 123074.59, "children": 123074.59, "infants": 123074.59}, "bags_price": {"1": 79.212, "2": 168.224}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 158, "hold_height": 52, "hold_length": 78, "hold_weight": 20, "hold_width": 28, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 3, "personal_item_width": 15}, "availability": {"seats": 6}, "airlines": ["FR", "IB"], "route": [{"id": "0b770a224c37000093465fe3_0", "combination_id": "0b770a224c37000093465fe3", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-03T13:25:00.000Z", "utc_arrival": "2023-06-03T11:25:00.000Z", "local_departure": "2023-06-03T10:05:00.000Z", "utc_departure": "2023-06-03T08:05:00.000Z"}, {"id": "0a220b774c3a0000fea059a3_0", "combination_id": "0a220b774c3a0000fea059a3", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "IB", "flight_no": 3278, "operating_carrier": "IB", "operating_flight_no": "3278", "fare_basis": "VZNNAOB4", "fare_category": "M", "fare_classes": "V", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-06T14:55:00.000Z", "utc_arrival": "2023-06-06T12:55:00.000Z", "local_departure": "2023-06-06T11:45:00.000Z", "utc_departure": "2023-06-06T09:45:00.000Z"}], "booking_token": "ELSiHDeooGw6FwF0HEzEltsAXejkRkgn8imh62X9EMArGCqckCaPS5xy7B-EEbL1d9nuu7pMqZQITb3p9AP0RM0pZS4z9uswzlRBY5WDH_-4LFgdJ8utKQPpDV0k3wH58BLw345aSoh8ab4bk7Z0Kvgv69oX0gmPRLpyCXIpth8JJ-mJFRP6Iyw7Yjo7yuQAylAknoxHb2z5jSjs8x7V2_1dwsd6Z4dcuibhvBd6dkLgwwHPvo06OLZJ8zk0NSGpOzqWWmkQ0xErnopMPovljhngHfFUYsUET0HcAzXJBBJC1z2laFTOhYePTcf0H44JIoDcCJxMKmyIt2wc_BV-35zov6npZqixm8QT2NuyxbDOCTFg8N3aJlygVmWmK8IA2EkNhMO9HrE8kyrL6ZW5bMctMuwtE14EA7ssJNIbPvAn-0iXZ0QK4RtJWFPHhFpdnqRo6npSO_ovncnky6OiQy7aACnCBDOJfPWswhwhHYZqgjESU58cLh9ISOiIL6lE7sX13SnhlXgvNubjU-WklCWqgsHcoxqEJfs8qJ06Z54ggmglaCICJLHg0hqxaN2ibHhpmQ1QLCMop2KzfsNzT4d5XbCBhRyZ0VlBkuTDDCIzd7nwh-E71ruVhfi81o_pwdRZaiu4OVM4V0Hl8uevBZtutSqDMFXodCzQPlh1MjJmV0b6Pm66Vz-ESjWMRofCaXNFgwMBCBfHTTy6XqOjo4aJSgcie39Tz2_BzJE-Ug0A=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c37000093465fe3_0%7C0a220b774c3a0000fea059a3_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=ELSiHDeooGw6FwF0HEzEltsAXejkRkgn8imh62X9EMArGCqckCaPS5xy7B-EEbL1d9nuu7pMqZQITb3p9AP0RM0pZS4z9uswzlRBY5WDH_-4LFgdJ8utKQPpDV0k3wH58BLw345aSoh8ab4bk7Z0Kvgv69oX0gmPRLpyCXIpth8JJ-mJFRP6Iyw7Yjo7yuQAylAknoxHb2z5jSjs8x7V2_1dwsd6Z4dcuibhvBd6dkLgwwHPvo06OLZJ8zk0NSGpOzqWWmkQ0xErnopMPovljhngHfFUYsUET0HcAzXJBBJC1z2laFTOhYePTcf0H44JIoDcCJxMKmyIt2wc_BV-35zov6npZqixm8QT2NuyxbDOCTFg8N3aJlygVmWmK8IA2EkNhMO9HrE8kyrL6ZW5bMctMuwtE14EA7ssJNIbPvAn-0iXZ0QK4RtJWFPHhFpdnqRo6npSO_ovncnky6OiQy7aACnCBDOJfPWswhwhHYZqgjESU58cLh9ISOiIL6lE7sX13SnhlXgvNubjU-WklCWqgsHcoxqEJfs8qJ06Z54ggmglaCICJLHg0hqxaN2ibHhpmQ1QLCMop2KzfsNzT4d5XbCBhRyZ0VlBkuTDDCIzd7nwh-E71ruVhfi81o_pwdRZaiu4OVM4V0Hl8uevBZtutSqDMFXodCzQPlh1MjJmV0b6Pm66Vz-ESjWMRofCaXNFgwMBCBfHTTy6XqOjo4aJSgcie39Tz2_BzJE-Ug0A=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-03T13:25:00.000Z", "utc_arrival": "2023-06-03T11:25:00.000Z", "local_departure": "2023-06-03T10:05:00.000Z", "utc_departure": "2023-06-03T08:05:00.000Z"}, {"id": "0b770a224c2b00006e021a7d_0|0a220b774c2f0000a02e0875_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 799.783054, "distance": 1975.87, "duration": {"departure": 12600, "return": 11400, "total": 24000}, "price": 246438.8132, "conversion": {"EUR": 645.116774, "HUF": 246438.8132}, "fare": {"adults": 123219.41, "children": 131530.32, "infants": 131530.32}, "bags_price": {"1": 85.4, "2": 170.786}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 7}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224c2b00006e021a7d_0", "combination_id": "0b770a224c2b00006e021a7d", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-22T19:45:00.000Z", "utc_arrival": "2023-05-22T17:45:00.000Z", "local_departure": "2023-05-22T16:15:00.000Z", "utc_departure": "2023-05-22T14:15:00.000Z"}, {"id": "0a220b774c2f0000a02e0875_0", "combination_id": "0a220b774c2f0000a02e0875", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-26T18:00:00.000Z", "utc_arrival": "2023-05-26T16:00:00.000Z", "local_departure": "2023-05-26T14:50:00.000Z", "utc_departure": "2023-05-26T12:50:00.000Z"}], "booking_token": "E3G8cvqJ81qiNLI8xdTsqchVVNdf-1THYj4RTmenkSWiyxvsnze09wDrtU9-E_VP0yBRz8q8oP7ms8dQOo5KMOob3rB0BHrCOzIv3CtOTtBMl42M6zWZX0mELBPpuwFPPTFD-xswx8uKHx8IcO8kKQHFyHPX-xtzde8GuQ94W9I57aVfracUgayjg7ONizXlXacRrLY0j5iYQbW2ALdsNuUs6IztIclTrWYs0pzk0lm9nTg1ly0TqFIIWPfR_MDGhDgNkAaQASRrzn95IXLhlbUwxHIjg7LXA63zCB5tPeyycdeocLK-CR8kKeE4vOaTGVA1en0cHbWsoBzMjdYVaAtp9LGhEfbjqx2KYV-fuzhEaF7w_96jUiVsUwAqCC0NxdIYxK3VZqarPldkICBMpLjudbaBkVf40MpeL6Yx_4QNSQotiXKPZUX1ynWS13ntc4hLfIIAuYH_g6FTmr25kSA28kcM8WqhgEL0XrU91WJUEIhs28swBZ-7fQpm3HiL3_OVxL0N1DzeIIjuTFmC140MwEwx2q1oFsztGXQIIN48381cbnLD0u2IRo4MFHr4x3gkrJN8HshD4sSxcORK0-KY3l16VSD9lx4db7yojx-4p0k0ll3lbjxd0SAg1Q9mEP10UT16WPBNV99bcoHxmSkPC9NtKjiWI6bxSdIJVvhSAAkGwNyVJBf2v288cbqlG2dNlSL3snj7LwEWjg9EAs4EsedIpGwPaPWllh3w7pUSMXyzJU5u3FxhkZyyaKLBxzj4EsuXQtsXG_Ofu2s0QnHbjVkC5y4GvRbR08fQMjjc=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c2b00006e021a7d_0%7C0a220b774c2f0000a02e0875_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=E3G8cvqJ81qiNLI8xdTsqchVVNdf-1THYj4RTmenkSWiyxvsnze09wDrtU9-E_VP0yBRz8q8oP7ms8dQOo5KMOob3rB0BHrCOzIv3CtOTtBMl42M6zWZX0mELBPpuwFPPTFD-xswx8uKHx8IcO8kKQHFyHPX-xtzde8GuQ94W9I57aVfracUgayjg7ONizXlXacRrLY0j5iYQbW2ALdsNuUs6IztIclTrWYs0pzk0lm9nTg1ly0TqFIIWPfR_MDGhDgNkAaQASRrzn95IXLhlbUwxHIjg7LXA63zCB5tPeyycdeocLK-CR8kKeE4vOaTGVA1en0cHbWsoBzMjdYVaAtp9LGhEfbjqx2KYV-fuzhEaF7w_96jUiVsUwAqCC0NxdIYxK3VZqarPldkICBMpLjudbaBkVf40MpeL6Yx_4QNSQotiXKPZUX1ynWS13ntc4hLfIIAuYH_g6FTmr25kSA28kcM8WqhgEL0XrU91WJUEIhs28swBZ-7fQpm3HiL3_OVxL0N1DzeIIjuTFmC140MwEwx2q1oFsztGXQIIN48381cbnLD0u2IRo4MFHr4x3gkrJN8HshD4sSxcORK0-KY3l16VSD9lx4db7yojx-4p0k0ll3lbjxd0SAg1Q9mEP10UT16WPBNV99bcoHxmSkPC9NtKjiWI6bxSdIJVvhSAAkGwNyVJBf2v288cbqlG2dNlSL3snj7LwEWjg9EAs4EsedIpGwPaPWllh3w7pUSMXyzJU5u3FxhkZyyaKLBxzj4EsuXQtsXG_Ofu2s0QnHbjVkC5y4GvRbR08fQMjjc=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-22T19:45:00.000Z", "utc_arrival": "2023-05-22T17:45:00.000Z", "local_departure": "2023-05-22T16:15:00.000Z", "utc_departure": "2023-05-22T14:15:00.000Z"}, {"id": "0b770a224c280000d84fb6b2_0|0a220b774c2b0000f0938698_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 801.855305, "distance": 1975.87, "duration": {"departure": 12600, "return": 11700, "total": 24300}, "price": 246721.0858, "conversion": {"EUR": 645.855695, "HUF": 246721.0858}, "fare": {"adults": 123360.54, "children": 123360.54, "infants": 123360.54}, "bags_price": {"1": 97.818, "2": 195.65}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 439, "hold_height": 149, "hold_length": 171, "hold_weight": 20, "hold_width": 119, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 3}, "airlines": ["W6"], "route": [{"id": "0b770a224c280000d84fb6b2_0", "combination_id": "0b770a224c280000d84fb6b2", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-19T19:45:00.000Z", "utc_arrival": "2023-05-19T17:45:00.000Z", "local_departure": "2023-05-19T16:15:00.000Z", "utc_departure": "2023-05-19T14:15:00.000Z"}, {"id": "0a220b774c2b0000f0938698_0", "combination_id": "0a220b774c2b0000f0938698", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "HREG", "fare_category": "M", "fare_classes": "H", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-22T23:45:00.000Z", "utc_arrival": "2023-05-22T21:45:00.000Z", "local_departure": "2023-05-22T20:30:00.000Z", "utc_departure": "2023-05-22T18:30:00.000Z"}], "booking_token": "EpK4Qb5KQGYqKQIdR4okUUpiCR1MZ5m0bg2r5QnxVlQhuAPi_qWxSJ2kfLbcX4Wh-HXj0AYy6ZkzU8pA5BTDLPKpiwbqYyaPjTiEl23maNWYOXjrZH6QLwfkozqgfBfxoCKjRlX-K6I5QfDNhKzfB1XuzhNsEupZGgHn45isLxxMDLM_BC_B-VJ-rvqnczlQ8hqw3JRcrynLBJpVvNsb5Glu38XbsPIEIqOA-pJe0WJr4O0LYH6rVfFtYq8APt9s7pFNhQ8QxvMx5eKsCQWTlSf32jSkkK99pZIz9buaR1FvP___1WYRww2mn-txPtruGnDM9VBNjyJgrl7F6biU_4QxWK-x6C0mPklM1YjRBdZG78BjInyMVh2lcaaKMnHU3PmU0rdqk8PJxSM5ZAK-LP10wsqDXZpxWjXKa2xXg88mPwODWs2EIKpU3rbzMKBbeBmkBUZSfhwQYngSwIfdnQE1wlh6iW_pTpHEfRIY4sqw_QOOe3YSw93EPBeNs1RBOKXW6kqih7JXQFo2DLXjC816Kg5Y5unAvQfTTEnO7n6XhvGAcwdfp5BAXkujKabctYFVyoo_b_KpV2f7-gZP667CxVcQHoVk601E6iPS8TUgc_n8ffXgsvonHPE0gJBXr659LiGA6KJrRW5NRjQc9W--CjToRryKr_izyOr282PFeXWItDV3PrmTTgKKt-SAnU0aB5nRbgpIP44RPsEz1kz0V19mOOkD3_2Dro1ogHNzpKc9xWdu65Vsl0E_D3jLFQlFsyr7g4JD16saU7zdRWEFBVgRUQHV9IdA_JLgxoWI=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c280000d84fb6b2_0%7C0a220b774c2b0000f0938698_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EpK4Qb5KQGYqKQIdR4okUUpiCR1MZ5m0bg2r5QnxVlQhuAPi_qWxSJ2kfLbcX4Wh-HXj0AYy6ZkzU8pA5BTDLPKpiwbqYyaPjTiEl23maNWYOXjrZH6QLwfkozqgfBfxoCKjRlX-K6I5QfDNhKzfB1XuzhNsEupZGgHn45isLxxMDLM_BC_B-VJ-rvqnczlQ8hqw3JRcrynLBJpVvNsb5Glu38XbsPIEIqOA-pJe0WJr4O0LYH6rVfFtYq8APt9s7pFNhQ8QxvMx5eKsCQWTlSf32jSkkK99pZIz9buaR1FvP___1WYRww2mn-txPtruGnDM9VBNjyJgrl7F6biU_4QxWK-x6C0mPklM1YjRBdZG78BjInyMVh2lcaaKMnHU3PmU0rdqk8PJxSM5ZAK-LP10wsqDXZpxWjXKa2xXg88mPwODWs2EIKpU3rbzMKBbeBmkBUZSfhwQYngSwIfdnQE1wlh6iW_pTpHEfRIY4sqw_QOOe3YSw93EPBeNs1RBOKXW6kqih7JXQFo2DLXjC816Kg5Y5unAvQfTTEnO7n6XhvGAcwdfp5BAXkujKabctYFVyoo_b_KpV2f7-gZP667CxVcQHoVk601E6iPS8TUgc_n8ffXgsvonHPE0gJBXr659LiGA6KJrRW5NRjQc9W--CjToRryKr_izyOr282PFeXWItDV3PrmTTgKKt-SAnU0aB5nRbgpIP44RPsEz1kz0V19mOOkD3_2Dro1ogHNzpKc9xWdu65Vsl0E_D3jLFQlFsyr7g4JD16saU7zdRWEFBVgRUQHV9IdA_JLgxoWI=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-19T19:45:00.000Z", "utc_arrival": "2023-05-19T17:45:00.000Z", "local_departure": "2023-05-19T16:15:00.000Z", "utc_departure": "2023-05-19T14:15:00.000Z"}, {"id": "0b770a224c050000101ee0e9_0|0a220b774c0800003a297c03_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 802.98718, "distance": 1975.87, "duration": {"departure": 12600, "return": 11400, "total": 24000}, "price": 247662.8102, "conversion": {"EUR": 648.3209, "HUF": 247662.8102}, "fare": {"adults": 123831.41, "children": 123831.41, "infants": 123831.41}, "bags_price": {"1": 112.252, "2": 224.504}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 3}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224c050000101ee0e9_0", "combination_id": "0b770a224c050000101ee0e9", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-14T19:45:00.000Z", "utc_arrival": "2023-04-14T17:45:00.000Z", "local_departure": "2023-04-14T16:15:00.000Z", "utc_departure": "2023-04-14T14:15:00.000Z"}, {"id": "0a220b774c0800003a297c03_0", "combination_id": "0a220b774c0800003a297c03", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-17T10:15:00.000Z", "utc_arrival": "2023-04-17T08:15:00.000Z", "local_departure": "2023-04-17T07:05:00.000Z", "utc_departure": "2023-04-17T05:05:00.000Z"}], "booking_token": "EqpyB21UMv2rG8tws4YvUMvaXWDKQ9r_Ou5JQqN-U2RC7phBXh_XOard9UnKN8vD2ikN27iB3sxtLOU8Xe51ImFr7ZmXchLJ6fyOIZ4oQuovWPGeLTIiz04OC_w7H6B4_o7Su8Z0syv6WLcfSI7QIG7xNqsFGa0NqFs31Dn0QVGmVe7qYZ6N97AL8wu0N13FYQHo5uwuMf2SvSf0jWHYGXyU-08mV_Xv1TJ_tGTVtPh0zkBKN6vx07xXG3ePg9Fmf87T-IuLgYosZ3AK0ivpIyTZKYZBDUylCc-l2b8hUQo9tJdpMB5GTJHMTtk5kb1dPTh-9m9Q3I_R5160wXFOWvH6U0lqiw3ssndegqXMGH7-tDbUsLZLALetdOGSWmQj51p_BNLUux4LhhYd8UD0M65NMggFMB9KhA6uAIhEoULyMq_sCR4pn3C4XtTBreVMS8xcsqGtkJrKTqhMfntWvS7i2ZUsTu3EPAAgvO3SX1bM32opCW_XgRYNJee4LKRUUt-fsRV-BaQMNRk25ft2NtIQlWroSe-mESgIc3F-7zl08VPrY3BYMa6dy8KHUl2h-sK-ZZuhRcCk7CIy1SYIsRyVa54FmpUdLrOf0DUsKlrxWXK1hhU_TnSPtgrO0k0wvvdnGLZQkGyJDbGKESBook_NJpe4ooQvduXMM9cVMOX4x3qPZyYJmGfWaCney9z6bsyGaH5hVDIYneAHrMeJwOd4aSblACHLYCdUf4fQGU5NoLQM1u0VUPitgdcXluIDFoTpjX5l_w5I_iVL0HPjM0A==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c050000101ee0e9_0%7C0a220b774c0800003a297c03_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EqpyB21UMv2rG8tws4YvUMvaXWDKQ9r_Ou5JQqN-U2RC7phBXh_XOard9UnKN8vD2ikN27iB3sxtLOU8Xe51ImFr7ZmXchLJ6fyOIZ4oQuovWPGeLTIiz04OC_w7H6B4_o7Su8Z0syv6WLcfSI7QIG7xNqsFGa0NqFs31Dn0QVGmVe7qYZ6N97AL8wu0N13FYQHo5uwuMf2SvSf0jWHYGXyU-08mV_Xv1TJ_tGTVtPh0zkBKN6vx07xXG3ePg9Fmf87T-IuLgYosZ3AK0ivpIyTZKYZBDUylCc-l2b8hUQo9tJdpMB5GTJHMTtk5kb1dPTh-9m9Q3I_R5160wXFOWvH6U0lqiw3ssndegqXMGH7-tDbUsLZLALetdOGSWmQj51p_BNLUux4LhhYd8UD0M65NMggFMB9KhA6uAIhEoULyMq_sCR4pn3C4XtTBreVMS8xcsqGtkJrKTqhMfntWvS7i2ZUsTu3EPAAgvO3SX1bM32opCW_XgRYNJee4LKRUUt-fsRV-BaQMNRk25ft2NtIQlWroSe-mESgIc3F-7zl08VPrY3BYMa6dy8KHUl2h-sK-ZZuhRcCk7CIy1SYIsRyVa54FmpUdLrOf0DUsKlrxWXK1hhU_TnSPtgrO0k0wvvdnGLZQkGyJDbGKESBook_NJpe4ooQvduXMM9cVMOX4x3qPZyYJmGfWaCney9z6bsyGaH5hVDIYneAHrMeJwOd4aSblACHLYCdUf4fQGU5NoLQM1u0VUPitgdcXluIDFoTpjX5l_w5I_iVL0HPjM0A==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-04-14T19:45:00.000Z", "utc_arrival": "2023-04-14T17:45:00.000Z", "local_departure": "2023-04-14T16:15:00.000Z", "utc_departure": "2023-04-14T14:15:00.000Z"}, {"id": "0b770a224c1f00002a8dc654_0|0a220b774c220000a4dc2bfb_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 800.125709, "distance": 1975.87, "duration": {"departure": 11700, "return": 11400, "total": 23100}, "price": 248097.7319, "conversion": {"EUR": 649.459419, "HUF": 248097.7319}, "fare": {"adults": 124048.87, "children": 128049.99, "infants": 128049.99}, "bags_price": {"1": 74.886, "2": 159.572}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 158, "hold_height": 52, "hold_length": 78, "hold_weight": 20, "hold_width": 28, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 3, "personal_item_width": 15}, "availability": {"seats": null}, "airlines": ["FR", "IB"], "route": [{"id": "0b770a224c1f00002a8dc654_0", "combination_id": "0b770a224c1f00002a8dc654", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "IB", "flight_no": 3279, "operating_carrier": "IB", "operating_flight_no": "3279", "fare_basis": "NZNNAOB4", "fare_category": "M", "fare_classes": "N", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-10T18:50:00.000Z", "utc_arrival": "2023-05-10T16:50:00.000Z", "local_departure": "2023-05-10T15:35:00.000Z", "utc_departure": "2023-05-10T13:35:00.000Z"}, {"id": "0a220b774c220000a4dc2bfb_0", "combination_id": "0a220b774c220000a4dc2bfb", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-13T09:40:00.000Z", "utc_arrival": "2023-05-13T07:40:00.000Z", "local_departure": "2023-05-13T06:30:00.000Z", "utc_departure": "2023-05-13T04:30:00.000Z"}], "booking_token": "EeVDU8wdBnmVDQ-YtzQa2EpFmI55XHLzW0cvbN9RLGyzVVHBLbFyyz6qGS0sahSgXez1Zm_ARZhZ80yxasepDf8An123Ri88IKH2ivOOFFpykaTm3VHlaEV4G_hhOiSw96SdhXYtZFyhD5yvvBfrvUwLVWXSXUeAr8NPUVb6dwgd46ItX1CP5uFKkzXZkusMFyM6hWHaPDzUefjGaBqLCh7J_mfntQ3Xr200kbhtOiTKsnIevqrQLU9Op1uV1NgWp6BwfcsDM9xNhi99gM06C7MC9J7RsMWyfj7jZxl3HE1fAwfOOJjD-4r8CH4yoLqtz2wCTUJMxgpHLcaeskK1qxTtLAS1qnAMtHcVOiRuG0oZbnBsJ2LP9jbvKWOZbpFAtPYSpyFj2tuht64gHjlMAfHqsGabiBvyb9x81_Yg9L39kuCNHjNuFmQ2IDTuG_I5lJPyYVMBTJ-sgEW03hBn71HrO57nfbPhxvQpK-5Q-ri9RXRumxl7VPGEIDj3H73G9__QyQyWFPxpeWEAHe-LPVQSkif5WwVmYI2_Jv4wJqlvY_NUpbcqYDAbjNh4AyMDm4-BjRtnAyGyXe0UXgNa7rY_BuMoDXVm_y5W5h9GlUEd6JG57a4-Juofx3Ta6TiaMXuTdtWYkxO9wdEOj7bAdZYX82P34v0Lr6bjR8hYv9n94NE-YB8ygl4hEzVUjg1S-a-ESC0G6uCVF_fdBJHl2EdkjpsFKBWiMQN2OBl3kZVSRwSqTXd3lj7SVuTR-Ganj", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c1f00002a8dc654_0%7C0a220b774c220000a4dc2bfb_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EeVDU8wdBnmVDQ-YtzQa2EpFmI55XHLzW0cvbN9RLGyzVVHBLbFyyz6qGS0sahSgXez1Zm_ARZhZ80yxasepDf8An123Ri88IKH2ivOOFFpykaTm3VHlaEV4G_hhOiSw96SdhXYtZFyhD5yvvBfrvUwLVWXSXUeAr8NPUVb6dwgd46ItX1CP5uFKkzXZkusMFyM6hWHaPDzUefjGaBqLCh7J_mfntQ3Xr200kbhtOiTKsnIevqrQLU9Op1uV1NgWp6BwfcsDM9xNhi99gM06C7MC9J7RsMWyfj7jZxl3HE1fAwfOOJjD-4r8CH4yoLqtz2wCTUJMxgpHLcaeskK1qxTtLAS1qnAMtHcVOiRuG0oZbnBsJ2LP9jbvKWOZbpFAtPYSpyFj2tuht64gHjlMAfHqsGabiBvyb9x81_Yg9L39kuCNHjNuFmQ2IDTuG_I5lJPyYVMBTJ-sgEW03hBn71HrO57nfbPhxvQpK-5Q-ri9RXRumxl7VPGEIDj3H73G9__QyQyWFPxpeWEAHe-LPVQSkif5WwVmYI2_Jv4wJqlvY_NUpbcqYDAbjNh4AyMDm4-BjRtnAyGyXe0UXgNa7rY_BuMoDXVm_y5W5h9GlUEd6JG57a4-Juofx3Ta6TiaMXuTdtWYkxO9wdEOj7bAdZYX82P34v0Lr6bjR8hYv9n94NE-YB8ygl4hEzVUjg1S-a-ESC0G6uCVF_fdBJHl2EdkjpsFKBWiMQN2OBl3kZVSRwSqTXd3lj7SVuTR-Ganj", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-10T18:50:00.000Z", "utc_arrival": "2023-05-10T16:50:00.000Z", "local_departure": "2023-05-10T15:35:00.000Z", "utc_departure": "2023-05-10T13:35:00.000Z"}, {"id": "0b770a224c1300004dd80c68_0|0a220b774c1600007449e031_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 802.714092, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 248577.1703, "conversion": {"EUR": 650.714472, "HUF": 248577.1703}, "fare": {"adults": 124288.59, "children": 124288.59, "infants": 124288.59}, "bags_price": {"1": 71.75, "2": 141.932}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 3}, "airlines": ["FR"], "route": [{"id": "0b770a224c1300004dd80c68_0", "combination_id": "0b770a224c1300004dd80c68", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-28T21:45:00.000Z", "utc_arrival": "2023-04-28T19:45:00.000Z", "local_departure": "2023-04-28T18:25:00.000Z", "utc_departure": "2023-04-28T16:25:00.000Z"}, {"id": "0a220b774c1600007449e031_0", "combination_id": "0a220b774c1600007449e031", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-01T10:15:00.000Z", "utc_arrival": "2023-05-01T08:15:00.000Z", "local_departure": "2023-05-01T07:05:00.000Z", "utc_departure": "2023-05-01T05:05:00.000Z"}], "booking_token": "EiXLkbqO_rfl704VbiztjzA_qhbZhGgelt7os1IuirUl8OFaKqz1_-Ow-yeNLIaxtB35NUTQtAzUe9mbftrYX6L5sARZs4KAG9DH9W0tPFsK-P3M0QvmdIhFPmKcH_z2qdowHi2JB7CVTL5DOnGdP9Mn35MEZJyGtrinknW5o_rovtWG7lrrUOelUby2wHm95S1Ulh6wAZZZVumvn959TzLgkOvTjQ9Cv8aqChPgAvGGOkTodWrHDwQMkfJGxo7rInGVkwuUQCLjHqg8QZI73mBDYLiug-o7IiGy8mt5N8OHX8k3MXdLrLezw8WPfZgYQSm-_wt9jOZIkIKMQKuDxJHubKYQKacTWk7Fs2Z3ocmf1kfgrBeM5I3uaWCxdbj99Cw57_5BE475TmycnQUNogI5kODaK63eeCth8A9gGwJ8gTDQieogJ0hC1p8SOknOjANZcQmm-jo-nqehFF0IKEYWwOyg9ZARhMDHH_tdmJwffuG13yANs2mgVgtwGK8hKiU4YMnGwzyxJIQkXLYz0qJJVNFIfhTUGX47XpHs1iZ5TpQLJWvA0RmVvwN9r502PN-NNE9jGZelON4vehVk5rOa4gyo_zmHnCiOtYH6xlQONFP_PBcpgJRvuseFZdO17t7JQ7qtpm8O2N6rOCygWJMr_h861tMlTu21p9GBhd7Sg1XNGBtFMm7BrQg_MW5N8S-1ZC4No-HL-wdKcV7RBU0YjLYZQAmjMMuYiKPWiv69UOw9QVWsEne667vkoKOMmUL8TKRU4YHEecv9Js1jfoA==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c1300004dd80c68_0%7C0a220b774c1600007449e031_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EiXLkbqO_rfl704VbiztjzA_qhbZhGgelt7os1IuirUl8OFaKqz1_-Ow-yeNLIaxtB35NUTQtAzUe9mbftrYX6L5sARZs4KAG9DH9W0tPFsK-P3M0QvmdIhFPmKcH_z2qdowHi2JB7CVTL5DOnGdP9Mn35MEZJyGtrinknW5o_rovtWG7lrrUOelUby2wHm95S1Ulh6wAZZZVumvn959TzLgkOvTjQ9Cv8aqChPgAvGGOkTodWrHDwQMkfJGxo7rInGVkwuUQCLjHqg8QZI73mBDYLiug-o7IiGy8mt5N8OHX8k3MXdLrLezw8WPfZgYQSm-_wt9jOZIkIKMQKuDxJHubKYQKacTWk7Fs2Z3ocmf1kfgrBeM5I3uaWCxdbj99Cw57_5BE475TmycnQUNogI5kODaK63eeCth8A9gGwJ8gTDQieogJ0hC1p8SOknOjANZcQmm-jo-nqehFF0IKEYWwOyg9ZARhMDHH_tdmJwffuG13yANs2mgVgtwGK8hKiU4YMnGwzyxJIQkXLYz0qJJVNFIfhTUGX47XpHs1iZ5TpQLJWvA0RmVvwN9r502PN-NNE9jGZelON4vehVk5rOa4gyo_zmHnCiOtYH6xlQONFP_PBcpgJRvuseFZdO17t7JQ7qtpm8O2N6rOCygWJMr_h861tMlTu21p9GBhd7Sg1XNGBtFMm7BrQg_MW5N8S-1ZC4No-HL-wdKcV7RBU0YjLYZQAmjMMuYiKPWiv69UOw9QVWsEne667vkoKOMmUL8TKRU4YHEecv9Js1jfoA==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-04-28T21:45:00.000Z", "utc_arrival": "2023-04-28T19:45:00.000Z", "local_departure": "2023-04-28T18:25:00.000Z", "utc_departure": "2023-04-28T16:25:00.000Z"}, {"id": "0b770a224c1a0000e8ad793c_0|0a220b774c1d000091abd9a6_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 804.672947, "distance": 1975.87, "duration": {"departure": 12000, "return": 11700, "total": 23700}, "price": 248816.1249, "conversion": {"EUR": 651.339997, "HUF": 248816.1249}, "fare": {"adults": 124408.06, "children": 127270.26, "infants": 127270.26}, "bags_price": {"1": 72.366, "2": 144.746}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 6}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224c1a0000e8ad793c_0", "combination_id": "0b770a224c1a0000e8ad793c", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-05T21:45:00.000Z", "utc_arrival": "2023-05-05T19:45:00.000Z", "local_departure": "2023-05-05T18:25:00.000Z", "utc_departure": "2023-05-05T16:25:00.000Z"}, {"id": "0a220b774c1d000091abd9a6_0", "combination_id": "0a220b774c1d000091abd9a6", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "GREG", "fare_category": "M", "fare_classes": "G", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-08T23:45:00.000Z", "utc_arrival": "2023-05-08T21:45:00.000Z", "local_departure": "2023-05-08T20:30:00.000Z", "utc_departure": "2023-05-08T18:30:00.000Z"}], "booking_token": "Er_IDMW1lRRhptKnisbgM6v_6be-gvVyjvx6SuY5oOPD-lOORECnvvMkCpWElITyh8qE5RPbFRfJ7sd3_jcijSuxlQvcWsrDI6nGmfNS_Nsn1owhHEhN4FLWhdnRHqy78LH4XyhvFprOPlqo26uv1MYEYzt2d34zITaPZgAb4-SKv3iCW-le4YBG5S0exMWt5z4BXI10mgMevl_F5uhVWyWMzqjMHbaVwJvrqsSHRWChQ3IaF87xgqckEHVa6cXoPXgxJMOo6_Yg_wiWll3OuovspGVMHK-3tflceT2ouCFqSuKJzA_dXH2abytRKl7fuC1aAq8HObvYGiFVZ9AOSBcfXHpmYs6oQTsDdk4mRm5EjVfyph-lN96ir1evmXavrHiKLSkUIM69ekzuwr8EZf7YnZrLPBx89-K4dppnYqfazcXuQn7nPHQyJDN_lsEt3ye77ZozMbsvFbZf6bOBoPienPoh6cMhaGCHwUi0vWl22ylzzRbUkE91G0dvkC_DiSoJsBtwDnxu7ovW4DljE5QzT3wVfpAvxtC1K5tnx0w7SUQA-OL54evH8hVOlH1rBG1VwzpmyQ6DX4gvqeQLSrzWtoommLhzEIbWnGFGPWdsnCPaoM3FYfakhXsgruaQIhBC7eJ0rks2OTuhN8LvBkPPWwLGeIvnhv5ZDi2hI3uBvAQwzMZWil7I1nNnZO5LJDfZfcdMvd2puSxv3Xoo-eNMiO6ZJ8IUeBPb5BXz2c_eccLRrTp60k1yh__rXpthuTIizHPEdIcko0-NYOEd0aT80s9IqdzptuO1sxEhSx44=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c1a0000e8ad793c_0%7C0a220b774c1d000091abd9a6_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=Er_IDMW1lRRhptKnisbgM6v_6be-gvVyjvx6SuY5oOPD-lOORECnvvMkCpWElITyh8qE5RPbFRfJ7sd3_jcijSuxlQvcWsrDI6nGmfNS_Nsn1owhHEhN4FLWhdnRHqy78LH4XyhvFprOPlqo26uv1MYEYzt2d34zITaPZgAb4-SKv3iCW-le4YBG5S0exMWt5z4BXI10mgMevl_F5uhVWyWMzqjMHbaVwJvrqsSHRWChQ3IaF87xgqckEHVa6cXoPXgxJMOo6_Yg_wiWll3OuovspGVMHK-3tflceT2ouCFqSuKJzA_dXH2abytRKl7fuC1aAq8HObvYGiFVZ9AOSBcfXHpmYs6oQTsDdk4mRm5EjVfyph-lN96ir1evmXavrHiKLSkUIM69ekzuwr8EZf7YnZrLPBx89-K4dppnYqfazcXuQn7nPHQyJDN_lsEt3ye77ZozMbsvFbZf6bOBoPienPoh6cMhaGCHwUi0vWl22ylzzRbUkE91G0dvkC_DiSoJsBtwDnxu7ovW4DljE5QzT3wVfpAvxtC1K5tnx0w7SUQA-OL54evH8hVOlH1rBG1VwzpmyQ6DX4gvqeQLSrzWtoommLhzEIbWnGFGPWdsnCPaoM3FYfakhXsgruaQIhBC7eJ0rks2OTuhN8LvBkPPWwLGeIvnhv5ZDi2hI3uBvAQwzMZWil7I1nNnZO5LJDfZfcdMvd2puSxv3Xoo-eNMiO6ZJ8IUeBPb5BXz2c_eccLRrTp60k1yh__rXpthuTIizHPEdIcko0-NYOEd0aT80s9IqdzptuO1sxEhSx44=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-05T21:45:00.000Z", "utc_arrival": "2023-05-05T19:45:00.000Z", "local_departure": "2023-05-05T18:25:00.000Z", "utc_departure": "2023-05-05T16:25:00.000Z"}, {"id": "0b770a224bf000009aab5dae_0|0a220b774bf30000da5652ad_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 803.43758, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 248853.5474, "conversion": {"EUR": 651.43796, "HUF": 248853.5474}, "fare": {"adults": 124426.77, "children": 127589.12, "infants": 127589.12}, "bags_price": {"1": 95.704, "2": 191.422}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 2}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224bf000009aab5dae_0", "combination_id": "0b770a224bf000009aab5dae", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "HREG", "fare_category": "M", "fare_classes": "H", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-03-24T19:40:00.000Z", "utc_arrival": "2023-03-24T18:40:00.000Z", "local_departure": "2023-03-24T16:20:00.000Z", "utc_departure": "2023-03-24T15:20:00.000Z"}, {"id": "0a220b774bf30000da5652ad_0", "combination_id": "0a220b774bf30000da5652ad", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-03-27T10:15:00.000Z", "utc_arrival": "2023-03-27T08:15:00.000Z", "local_departure": "2023-03-27T07:05:00.000Z", "utc_departure": "2023-03-27T05:05:00.000Z"}], "booking_token": "ETa3hPhpWWjATQG6e9YuUAqjSGqwG4KGQWVmwNljzFgeeLU3G8fGX-EpRJnAh6-pCBFCmocqP_71KKp94EQCau-ZuQ3nniwJD5M453zfK_wWiiZQAUK7t_1A70JGgRHOnEn8IJzIxoi3eN3kFj2lx-ZvqI-OOEEMXi6tUOlPvDGuRhrUJLjpIs4Lj4OGNrXlF5MeaONrj0EqOmKQ7CMDNVhSREQkjY21FnQ8PlrVJcVsj9z1-6dmQwvkloBg0irIGVIOk2Szq-WswcNMJXYRSUmZu0wGDPoSw53L9Sqa7JU2Wh-U_A0D7YW0KEnkR8LAlNFmvdq6O2G6n2wOS-MSd6-PYiPSok3bg-5sZeUOCynix8b6zN9MV1SVp63k4-0ER4OMI4eO0I_oLVx2TtbOloiWhaWGsEvvkvtj8RVSWZgoPgQ7rmTKVcLPWi6Uxbz3orkU1kPdkuanwvU-EaPwkP5Bd-U8pYxSSEmPl7HP2nJi4KzjNzZq1rTAPXf3CdP2rJnGcnHHJ36cIpfDyWNaFTJW6NJYSS3b1T25rZpzr51ltXIeeiwVaxw0AWnZ4xCMfM8bHEpMZYdaW3Ypt9wujRJaBXEMjjE1sGPh3lS1_NkFYOsDCA2yT0j7BOs-hRmwOXo3o-OGThx6O5mk8nBG3KlBNyVCX6_U8sBQ-V02BYfMKVQPvfiGLkxOfMbebkb7hTlcXIGIdrEszj2zi5txXL2Wf3vBtbDx-k9m67b1PwuO5kc_ewjuictp5Z9LLjfAc8ug5hg--aHRz0V2yn9xsv4JeofD_mkkeNkWxXfMJ_ig=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224bf000009aab5dae_0%7C0a220b774bf30000da5652ad_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=ETa3hPhpWWjATQG6e9YuUAqjSGqwG4KGQWVmwNljzFgeeLU3G8fGX-EpRJnAh6-pCBFCmocqP_71KKp94EQCau-ZuQ3nniwJD5M453zfK_wWiiZQAUK7t_1A70JGgRHOnEn8IJzIxoi3eN3kFj2lx-ZvqI-OOEEMXi6tUOlPvDGuRhrUJLjpIs4Lj4OGNrXlF5MeaONrj0EqOmKQ7CMDNVhSREQkjY21FnQ8PlrVJcVsj9z1-6dmQwvkloBg0irIGVIOk2Szq-WswcNMJXYRSUmZu0wGDPoSw53L9Sqa7JU2Wh-U_A0D7YW0KEnkR8LAlNFmvdq6O2G6n2wOS-MSd6-PYiPSok3bg-5sZeUOCynix8b6zN9MV1SVp63k4-0ER4OMI4eO0I_oLVx2TtbOloiWhaWGsEvvkvtj8RVSWZgoPgQ7rmTKVcLPWi6Uxbz3orkU1kPdkuanwvU-EaPwkP5Bd-U8pYxSSEmPl7HP2nJi4KzjNzZq1rTAPXf3CdP2rJnGcnHHJ36cIpfDyWNaFTJW6NJYSS3b1T25rZpzr51ltXIeeiwVaxw0AWnZ4xCMfM8bHEpMZYdaW3Ypt9wujRJaBXEMjjE1sGPh3lS1_NkFYOsDCA2yT0j7BOs-hRmwOXo3o-OGThx6O5mk8nBG3KlBNyVCX6_U8sBQ-V02BYfMKVQPvfiGLkxOfMbebkb7hTlcXIGIdrEszj2zi5txXL2Wf3vBtbDx-k9m67b1PwuO5kc_ewjuictp5Z9LLjfAc8ug5hg--aHRz0V2yn9xsv4JeofD_mkkeNkWxXfMJ_ig=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-03-24T19:40:00.000Z", "utc_arrival": "2023-03-24T18:40:00.000Z", "local_departure": "2023-03-24T16:20:00.000Z", "utc_departure": "2023-03-24T15:20:00.000Z"}, {"id": "0b770a224c130000597a9e5b_0|0a220b774c1700007308efb9_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 807.449401, "distance": 1975.87, "duration": {"departure": 12600, "return": 11400, "total": 24000}, "price": 249367.4077, "conversion": {"EUR": 652.783121, "HUF": 249367.4077}, "fare": {"adults": 124683.7, "children": 124683.7, "infants": 124683.7}, "bags_price": {"1": 110.376, "2": 230.566}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 158, "hold_height": 52, "hold_length": 78, "hold_weight": 20, "hold_width": 28, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 3, "personal_item_width": 15}, "availability": {"seats": 3}, "airlines": ["W6", "IB"], "route": [{"id": "0b770a224c130000597a9e5b_0", "combination_id": "0b770a224c130000597a9e5b", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "KREG", "fare_category": "M", "fare_classes": "K", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-28T19:45:00.000Z", "utc_arrival": "2023-04-28T17:45:00.000Z", "local_departure": "2023-04-28T16:15:00.000Z", "utc_departure": "2023-04-28T14:15:00.000Z"}, {"id": "0a220b774c1700007308efb9_0", "combination_id": "0a220b774c1700007308efb9", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "IB", "flight_no": 3278, "operating_carrier": "IB", "operating_flight_no": "3278", "fare_basis": "SDNNAOB4", "fare_category": "M", "fare_classes": "S", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-02T14:55:00.000Z", "utc_arrival": "2023-05-02T12:55:00.000Z", "local_departure": "2023-05-02T11:45:00.000Z", "utc_departure": "2023-05-02T09:45:00.000Z"}], "booking_token": "EixNKKPlqOAqa6Tld8r1r02ENaRwTPOJF5TI8ugYQ5V1GUA5TImDf8HM6Q4ku9deklvW33kRLfoEvbteQMROdIK4ALUYohGZmEq2k2rrSRILGb78JIGoZcc9vYw2j0z6dsgtOvju127zkLxwcW3WSDZJHtJ2UPzfovuD2_Q1ttBvzfgSt9-KYr4WybwxLiPF3prPjEu2K7fMm7Xdpw_ol6plpIwUiOERqTmQtSUgN7gq9kPdItSh4j-8QqWeEXyZ2vu_oQeLK_bT4Hd-jDc-kpRkJSI6ci7sm4OKyatRanYDZg38vD2nRS-8VvfnhSNKryO8xDzRyyETtWOMS2kWVokqLxNBBJQ78CzA72ZHjM69Y0Lgj3d3BT05tUxC9e4eby4Y9IVNN9bwPcyzBm4hUya65QHRNvC4wDultpGFfugKApXsmseFy_fwRjT2he-sMSDws1ne2z0Shwz-pJT24ZLQrUc_bu8KZA3_zJK-9OqPieG-ii2-ZgDGwcmCKiGOECGd2AebuCUJ6bFKqVTGZBCJ2EJ9hUMPN2uMBvK_HoWslMLDTrF4gfxwgTaY_00DYt7my66bizc9frihEyIVqjrVTrDLNeADIvK42rj12a2iRDbkdcOfazHIYSHhJ_KPDVBcbt3gNq12eJiCQD4871Q14ePtfLS91u_8VAv2LM8Lkg0PYBB5VPfBPHRpPxuNFFEtWnEYyOS6tmGQGfj6JbV1P1u6m6OLDI0gukyB2b6hts70CBScghjzcjR-9dNL1y7aQgy2BrFTPWxWP7EHyBCYsgtVFdI2ZPxH8ty7vN0cfg60mdoKKi4nt_LMCl7Nw", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c130000597a9e5b_0%7C0a220b774c1700007308efb9_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EixNKKPlqOAqa6Tld8r1r02ENaRwTPOJF5TI8ugYQ5V1GUA5TImDf8HM6Q4ku9deklvW33kRLfoEvbteQMROdIK4ALUYohGZmEq2k2rrSRILGb78JIGoZcc9vYw2j0z6dsgtOvju127zkLxwcW3WSDZJHtJ2UPzfovuD2_Q1ttBvzfgSt9-KYr4WybwxLiPF3prPjEu2K7fMm7Xdpw_ol6plpIwUiOERqTmQtSUgN7gq9kPdItSh4j-8QqWeEXyZ2vu_oQeLK_bT4Hd-jDc-kpRkJSI6ci7sm4OKyatRanYDZg38vD2nRS-8VvfnhSNKryO8xDzRyyETtWOMS2kWVokqLxNBBJQ78CzA72ZHjM69Y0Lgj3d3BT05tUxC9e4eby4Y9IVNN9bwPcyzBm4hUya65QHRNvC4wDultpGFfugKApXsmseFy_fwRjT2he-sMSDws1ne2z0Shwz-pJT24ZLQrUc_bu8KZA3_zJK-9OqPieG-ii2-ZgDGwcmCKiGOECGd2AebuCUJ6bFKqVTGZBCJ2EJ9hUMPN2uMBvK_HoWslMLDTrF4gfxwgTaY_00DYt7my66bizc9frihEyIVqjrVTrDLNeADIvK42rj12a2iRDbkdcOfazHIYSHhJ_KPDVBcbt3gNq12eJiCQD4871Q14ePtfLS91u_8VAv2LM8Lkg0PYBB5VPfBPHRpPxuNFFEtWnEYyOS6tmGQGfj6JbV1P1u6m6OLDI0gukyB2b6hts70CBScghjzcjR-9dNL1y7aQgy2BrFTPWxWP7EHyBCYsgtVFdI2ZPxH8ty7vN0cfg60mdoKKi4nt_LMCl7Nw", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-04-28T19:45:00.000Z", "utc_arrival": "2023-04-28T17:45:00.000Z", "local_departure": "2023-04-28T16:15:00.000Z", "utc_departure": "2023-04-28T14:15:00.000Z"}, {"id": "0b770a224c390000c8acc8ed_0|0a220b774c3d0000e250d0cc_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 807.513609, "distance": 1975.87, "duration": {"departure": 12600, "return": 11400, "total": 24000}, "price": 249391.9356, "conversion": {"EUR": 652.847329, "HUF": 249391.9356}, "fare": {"adults": 124695.97, "children": 127878.13, "infants": 127878.13}, "bags_price": {"1": 92.61, "2": 185.234}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 6}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224c390000c8acc8ed_0", "combination_id": "0b770a224c390000c8acc8ed", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "HREG", "fare_category": "M", "fare_classes": "H", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-05T19:45:00.000Z", "utc_arrival": "2023-06-05T17:45:00.000Z", "local_departure": "2023-06-05T16:15:00.000Z", "utc_departure": "2023-06-05T14:15:00.000Z"}, {"id": "0a220b774c3d0000e250d0cc_0", "combination_id": "0a220b774c3d0000e250d0cc", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-09T18:00:00.000Z", "utc_arrival": "2023-06-09T16:00:00.000Z", "local_departure": "2023-06-09T14:50:00.000Z", "utc_departure": "2023-06-09T12:50:00.000Z"}], "booking_token": "EtOZ4SDHbhnvGsi55SFl1qxROZfkuwM_A2URvejkmGAyM_S2WI_m6Yl9F0YQq6cyJGQ2hsLo9_spbiud5nXonLmY0VHvMA0Y8_XrV_JaLMvdSClD_qzOF4GsCEjnTfTugm5aDGcoXNPoSUZPjBl8vmY-o2TtZe3dhxrMnZzT1mgc_Ahi--11KDVt3Y8M9g-I5LaSqqs1evYFLuVfxmC1mKhrxLhyVt3sZsgxjyDCKGM7mYhgiLpLIomE8bw9IIjDijxd5ioqLJGkFHOXtARLghVpIjfrZLwm0J0r1K2aVre1Jtbj6g-dDLkTOUD8lshfZ3HwBA87nDwEqPooYeOmMN3J9aLkNnXhSqgHfI2e3b4JPlSQN7ia5RP6rCvUAatwPPdLPP_MAcIG2UbEtUmJRDoRi0A61rlZyF8VoeUho7gQDf6LBmk41aQz9Td-QmvCoCZ5BSWjuh3PS4cw9KdZ-RV1xi1gjPqQSI6BSeSsBhPVpy6f-TaPiP7O-373vEO0V00EX9kiSyGS46lwe4C9TbM8jzpvLM4RHdDb7-xQGOOccfbOp8JohwOKA83RMuMSiq5MA9Pavv--pmzMtAjufoFMmaGi-e8yafdLZnVEc4QpESnrag83MaUGnX53t8vTw9xQwg-baG3WGVyphoD5Rd2SZW7NtkQJPaY6WQrqwlpNStFfpiFyOvB7FvvMC98e9l_nbquFB3qoTvBjCZmhK2aiYcZjEQVBaqwpm9F9S7uO_hq3oVmHzweoV4elYWRwoeO43Cy94_nMpMp_S8kV-HckUgPYDoqs2vNNzimmkU_M=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c390000c8acc8ed_0%7C0a220b774c3d0000e250d0cc_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EtOZ4SDHbhnvGsi55SFl1qxROZfkuwM_A2URvejkmGAyM_S2WI_m6Yl9F0YQq6cyJGQ2hsLo9_spbiud5nXonLmY0VHvMA0Y8_XrV_JaLMvdSClD_qzOF4GsCEjnTfTugm5aDGcoXNPoSUZPjBl8vmY-o2TtZe3dhxrMnZzT1mgc_Ahi--11KDVt3Y8M9g-I5LaSqqs1evYFLuVfxmC1mKhrxLhyVt3sZsgxjyDCKGM7mYhgiLpLIomE8bw9IIjDijxd5ioqLJGkFHOXtARLghVpIjfrZLwm0J0r1K2aVre1Jtbj6g-dDLkTOUD8lshfZ3HwBA87nDwEqPooYeOmMN3J9aLkNnXhSqgHfI2e3b4JPlSQN7ia5RP6rCvUAatwPPdLPP_MAcIG2UbEtUmJRDoRi0A61rlZyF8VoeUho7gQDf6LBmk41aQz9Td-QmvCoCZ5BSWjuh3PS4cw9KdZ-RV1xi1gjPqQSI6BSeSsBhPVpy6f-TaPiP7O-373vEO0V00EX9kiSyGS46lwe4C9TbM8jzpvLM4RHdDb7-xQGOOccfbOp8JohwOKA83RMuMSiq5MA9Pavv--pmzMtAjufoFMmaGi-e8yafdLZnVEc4QpESnrag83MaUGnX53t8vTw9xQwg-baG3WGVyphoD5Rd2SZW7NtkQJPaY6WQrqwlpNStFfpiFyOvB7FvvMC98e9l_nbquFB3qoTvBjCZmhK2aiYcZjEQVBaqwpm9F9S7uO_hq3oVmHzweoV4elYWRwoeO43Cy94_nMpMp_S8kV-HckUgPYDoqs2vNNzimmkU_M=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-05T19:45:00.000Z", "utc_arrival": "2023-06-05T17:45:00.000Z", "local_departure": "2023-06-05T16:15:00.000Z", "utc_departure": "2023-06-05T14:15:00.000Z"}, {"id": "0b770a224c310000511137a9_0|0a220b774c35000063a8527d_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 813.406451, "distance": 1975.87, "duration": {"departure": 12600, "return": 11700, "total": 24300}, "price": 251133.6989, "conversion": {"EUR": 657.406841, "HUF": 251133.6989}, "fare": {"adults": 125566.85, "children": 128512.94, "infants": 128512.94}, "bags_price": {"1": 101.262, "2": 202.524}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 439, "hold_height": 149, "hold_length": 171, "hold_weight": 20, "hold_width": 119, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 5}, "airlines": ["W6"], "route": [{"id": "0b770a224c310000511137a9_0", "combination_id": "0b770a224c310000511137a9", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "GHREG", "fare_category": "M", "fare_classes": "G", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-28T17:05:00.000Z", "utc_arrival": "2023-05-28T15:05:00.000Z", "local_departure": "2023-05-28T13:35:00.000Z", "utc_departure": "2023-05-28T11:35:00.000Z"}, {"id": "0a220b774c35000063a8527d_0", "combination_id": "0a220b774c35000063a8527d", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "HIREG", "fare_category": "M", "fare_classes": "H", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-02T01:15:00.000Z", "utc_arrival": "2023-06-01T23:15:00.000Z", "local_departure": "2023-06-01T22:00:00.000Z", "utc_departure": "2023-06-01T20:00:00.000Z"}], "booking_token": "ENyioPScj2H4_M7u9_gAtSn7msxI-h6pAz-52E3qZTaykSUjuUDyMTn8p74DtlXB_QZT8s7Plo1rqYPfXh8WcYdUK2RitAXj4W4TuVZMmWLljTapll6SJ8tTCn8VPNeKKz4Oka-uEz5iGaW5l6FBcLFoSv0yu5o81NYfI249lPT3YQHRpOZu1Yuwz9EkyXs8lZblb74OGOEH8VId0c3k3BLJt9aUB63ISEjkSM-BYkR246wZzPTtCGELHmiSKk9Ds5PqOXkUTg_pxC52e-s0a-WPDdfewpVETTNNe2JQ4rJB6ZaqCHZkwJEMQLGGeMd9Bcoybb8vwd2MvW_WrnO1eit3Yo5mUV1a4vVY8WGBh8GjzLRMfytC8YjnssULt25WCrmYKu-0kRi4SCH8EL4kVrP3BeOorTo04AflD-WyuPmsJlTWRTEfDpHw5q_ODKWDYYI8PzADxQSYj7PyG_vbGxGQCAQEzzU9JY5fR69ncWttmq288-zWxEhHMHoKLBLMR2-7cJ5MtpajwcLWJ__juukCgFIIcUm-DXX4U1qzAoBZfUZUjvlNJjkiP4V4PFOPJQuhIg3AIOK6RQa5BhrG2jkZDrOrRHTy19la6ncSa4s2yLDwpnTcAcId_Lui1k7PnlXDGOfr69abKe-xYo94kpMXqs0MJ8_4pf-UsovuChNbPz4V2iKvGf7tHZWLlb_RbFOKlzSwF20wOiib31HXyYJVEyEOvIYUbEHCHJzdevfDmPtE9bzMH81xuz_BuijHCoUSaaL4C9gXF2jSekv8FIIKVsvYcIoUEvHnbfLMEpmE=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c310000511137a9_0%7C0a220b774c35000063a8527d_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=ENyioPScj2H4_M7u9_gAtSn7msxI-h6pAz-52E3qZTaykSUjuUDyMTn8p74DtlXB_QZT8s7Plo1rqYPfXh8WcYdUK2RitAXj4W4TuVZMmWLljTapll6SJ8tTCn8VPNeKKz4Oka-uEz5iGaW5l6FBcLFoSv0yu5o81NYfI249lPT3YQHRpOZu1Yuwz9EkyXs8lZblb74OGOEH8VId0c3k3BLJt9aUB63ISEjkSM-BYkR246wZzPTtCGELHmiSKk9Ds5PqOXkUTg_pxC52e-s0a-WPDdfewpVETTNNe2JQ4rJB6ZaqCHZkwJEMQLGGeMd9Bcoybb8vwd2MvW_WrnO1eit3Yo5mUV1a4vVY8WGBh8GjzLRMfytC8YjnssULt25WCrmYKu-0kRi4SCH8EL4kVrP3BeOorTo04AflD-WyuPmsJlTWRTEfDpHw5q_ODKWDYYI8PzADxQSYj7PyG_vbGxGQCAQEzzU9JY5fR69ncWttmq288-zWxEhHMHoKLBLMR2-7cJ5MtpajwcLWJ__juukCgFIIcUm-DXX4U1qzAoBZfUZUjvlNJjkiP4V4PFOPJQuhIg3AIOK6RQa5BhrG2jkZDrOrRHTy19la6ncSa4s2yLDwpnTcAcId_Lui1k7PnlXDGOfr69abKe-xYo94kpMXqs0MJ8_4pf-UsovuChNbPz4V2iKvGf7tHZWLlb_RbFOKlzSwF20wOiib31HXyYJVEyEOvIYUbEHCHJzdevfDmPtE9bzMH81xuz_BuijHCoUSaaL4C9gXF2jSekv8FIIKVsvYcIoUEvHnbfLMEpmE=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-28T17:05:00.000Z", "utc_arrival": "2023-05-28T15:05:00.000Z", "local_departure": "2023-05-28T13:35:00.000Z", "utc_departure": "2023-05-28T11:35:00.000Z"}, {"id": "0b770a224c3f0000d3040121_0|0a220b774c430000391b6c3b_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 814.144302, "distance": 1975.87, "duration": {"departure": 12600, "return": 11700, "total": 24300}, "price": 251415.5628, "conversion": {"EUR": 658.144692, "HUF": 251415.5628}, "fare": {"adults": 125707.78, "children": 125707.78, "infants": 125707.78}, "bags_price": {"1": 120.4, "2": 240.8}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 439, "hold_height": 149, "hold_length": 171, "hold_weight": 20, "hold_width": 119, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 2}, "airlines": ["W6"], "route": [{"id": "0b770a224c3f0000d3040121_0", "combination_id": "0b770a224c3f0000d3040121", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "GFREG", "fare_category": "M", "fare_classes": "G", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-11T17:05:00.000Z", "utc_arrival": "2023-06-11T15:05:00.000Z", "local_departure": "2023-06-11T13:35:00.000Z", "utc_departure": "2023-06-11T11:35:00.000Z"}, {"id": "0a220b774c430000391b6c3b_0", "combination_id": "0a220b774c430000391b6c3b", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "JREG", "fare_category": "M", "fare_classes": "J", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-16T01:15:00.000Z", "utc_arrival": "2023-06-15T23:15:00.000Z", "local_departure": "2023-06-15T22:00:00.000Z", "utc_departure": "2023-06-15T20:00:00.000Z"}], "booking_token": "EkWLXt9aF2JdyaRKOZF0E0q4Wy3Q-WmVaY-8N_Eg91AujYcwH4pXR433DHMzCVS8e_ie05gbB5Fx7A7N8zRPZFZvrxyamVnWfkox_3u4dtZ2370hNyiaGrX9AcCpmOBcQSygq7-JADDqiK4o-UuM6EdUhoaOK1B2TQHXV8UjGXbs5EavtXipPWNfKEHBtv2SyFb1mmV9DmUABlJixfmkUUQ1XdJJYrzyT1jYbYdk-BxaPzoPDLEHbBDuulBx6FNHEXQm0COARJdPhVy1yJWuISAoM_k_ILMlpq4DjbKV03wE6Ws6LnJEZUcLCoTF-32ebkZv5VI5PIFfa0EiXcsqEoevuTR2FURUiLl_9tRXoLe6QAUlCBjXAzuxTZe4OKSrz_7xlCO44DwRu5q9voOXCtYVZCvCsRVpH9QMKSGVS0UTM278zgxW-wMGu_cPTtMh7rApINKdUGwU2jZmhfjEFQZU8H5iUyFBPljj5XDvGzfgUFHj36PAAUTgqod_fmI39TeEJNns2KDVh3IHStqOYJImjOAmeZPuiGVoxTnHNDY1ktrAn_Jt0ZMi2YCxjZIdI1OMWBLr7BhUS6cJL2tA_iIcuW1T6vwFt7_W0B7twxg0fCcU31eN_heC0v2XMZfjfM0Pnv5HVapNgqnbcgS0CIXA3ug7l0nAIFtB_aNuCnOAyylTLT6_L4CQ2Ht-_AQ8wk2G8V72MiVGYq2u-smO3O5E2f6aOKULS49qNFgkiQl27t-EIzkFx5ahWLp73yuqpwTz7EotoqDfbymFrGYXczsUcPgYInuOstMyz0mX67Ls=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c3f0000d3040121_0%7C0a220b774c430000391b6c3b_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EkWLXt9aF2JdyaRKOZF0E0q4Wy3Q-WmVaY-8N_Eg91AujYcwH4pXR433DHMzCVS8e_ie05gbB5Fx7A7N8zRPZFZvrxyamVnWfkox_3u4dtZ2370hNyiaGrX9AcCpmOBcQSygq7-JADDqiK4o-UuM6EdUhoaOK1B2TQHXV8UjGXbs5EavtXipPWNfKEHBtv2SyFb1mmV9DmUABlJixfmkUUQ1XdJJYrzyT1jYbYdk-BxaPzoPDLEHbBDuulBx6FNHEXQm0COARJdPhVy1yJWuISAoM_k_ILMlpq4DjbKV03wE6Ws6LnJEZUcLCoTF-32ebkZv5VI5PIFfa0EiXcsqEoevuTR2FURUiLl_9tRXoLe6QAUlCBjXAzuxTZe4OKSrz_7xlCO44DwRu5q9voOXCtYVZCvCsRVpH9QMKSGVS0UTM278zgxW-wMGu_cPTtMh7rApINKdUGwU2jZmhfjEFQZU8H5iUyFBPljj5XDvGzfgUFHj36PAAUTgqod_fmI39TeEJNns2KDVh3IHStqOYJImjOAmeZPuiGVoxTnHNDY1ktrAn_Jt0ZMi2YCxjZIdI1OMWBLr7BhUS6cJL2tA_iIcuW1T6vwFt7_W0B7twxg0fCcU31eN_heC0v2XMZfjfM0Pnv5HVapNgqnbcgS0CIXA3ug7l0nAIFtB_aNuCnOAyylTLT6_L4CQ2Ht-_AQ8wk2G8V72MiVGYq2u-smO3O5E2f6aOKULS49qNFgkiQl27t-EIzkFx5ahWLp73yuqpwTz7EotoqDfbymFrGYXczsUcPgYInuOstMyz0mX67Ls=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-11T17:05:00.000Z", "utc_arrival": "2023-06-11T15:05:00.000Z", "local_departure": "2023-06-11T13:35:00.000Z", "utc_departure": "2023-06-11T11:35:00.000Z"}, {"id": "0b770a224c210000fa6546ee_0|0a220b774c250000060d8840_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 813.961789, "distance": 1975.87, "duration": {"departure": 12600, "return": 11400, "total": 24000}, "price": 251855.1824, "conversion": {"EUR": 659.295509, "HUF": 251855.1824}, "fare": {"adults": 125927.59, "children": 125927.59, "infants": 125927.59}, "bags_price": {"1": 81.242, "2": 162.498}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 4}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224c210000fa6546ee_0", "combination_id": "0b770a224c210000fa6546ee", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "GFREG", "fare_category": "M", "fare_classes": "G", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-12T19:45:00.000Z", "utc_arrival": "2023-05-12T17:45:00.000Z", "local_departure": "2023-05-12T16:15:00.000Z", "utc_departure": "2023-05-12T14:15:00.000Z"}, {"id": "0a220b774c250000060d8840_0", "combination_id": "0a220b774c250000060d8840", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-16T14:05:00.000Z", "utc_arrival": "2023-05-16T12:05:00.000Z", "local_departure": "2023-05-16T10:55:00.000Z", "utc_departure": "2023-05-16T08:55:00.000Z"}], "booking_token": "E2e7sgDU73p7ntQKUKutC81CY1TXz4i0kuEGBXVW1v-B3dHeuYqr5KBUkgc5IpDf9_qww-YTekdsJZa34ih70_1wp2tAnNrS_420hTFVIjz2ntrvPXux6osonkmcj1vfbePUsKEp5XLVr3ckOSElupt0fO2vxFhAz7UqIziTVhbktYLKCDDnd8GBmCrMubdMSqBsE-XAt2CG8EptNpNtOxlEG_02ngM4qYRKTWeoeOmGTejp871OnZbbtHMMso-z-VWgMMknDQINZ03f1XPp0iPkE_ranyxDAj8siMTYbZMxLv4yXWRPIIiCiSJukKXAVBF1biTZPzybH9CJ5ipOog9doe1yJmunfmSUh-iIGnhn0OowD6915oatCF7V4Vr-KFXH60vN8kD-pHHcfxAKl7huITCxuvpa3RPin6tOwh8hP18TdzzHwF-f8YEhtN1jqpjEMZRIH8Dq0iWOqIV-hbnEu8tS8IsVSKWsshyjMiVS_miJMoPpiSMlKXk9I-ZYKO6Ja7XaCJknP6HOxFRSwpMZ_bfpxf4fWuXUtNO8xqe3Aqk8aVPjJVBVYe_a6iJNTYwh_qZOaYCc_4wDt-0x9EQPrZpK0PuMx_ldD6BnO-B4uMai6fNB80k0IiMYmvb2A63VrajQB4GU54COQJOPbi5zTAWK13R4yLSqJznR0QEppGxldfpLWA5UPWzUqgzBa6BUJgNmrkjHlSRe47cFedzrAD-_mr3rVAjZRkzdYVfyUsVGMvm9-fvI4a_l73opAJZOPhrZqxnMG7BrjgVhQrndeZlnPopfPQ4Hilp6RzBg=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c210000fa6546ee_0%7C0a220b774c250000060d8840_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=E2e7sgDU73p7ntQKUKutC81CY1TXz4i0kuEGBXVW1v-B3dHeuYqr5KBUkgc5IpDf9_qww-YTekdsJZa34ih70_1wp2tAnNrS_420hTFVIjz2ntrvPXux6osonkmcj1vfbePUsKEp5XLVr3ckOSElupt0fO2vxFhAz7UqIziTVhbktYLKCDDnd8GBmCrMubdMSqBsE-XAt2CG8EptNpNtOxlEG_02ngM4qYRKTWeoeOmGTejp871OnZbbtHMMso-z-VWgMMknDQINZ03f1XPp0iPkE_ranyxDAj8siMTYbZMxLv4yXWRPIIiCiSJukKXAVBF1biTZPzybH9CJ5ipOog9doe1yJmunfmSUh-iIGnhn0OowD6915oatCF7V4Vr-KFXH60vN8kD-pHHcfxAKl7huITCxuvpa3RPin6tOwh8hP18TdzzHwF-f8YEhtN1jqpjEMZRIH8Dq0iWOqIV-hbnEu8tS8IsVSKWsshyjMiVS_miJMoPpiSMlKXk9I-ZYKO6Ja7XaCJknP6HOxFRSwpMZ_bfpxf4fWuXUtNO8xqe3Aqk8aVPjJVBVYe_a6iJNTYwh_qZOaYCc_4wDt-0x9EQPrZpK0PuMx_ldD6BnO-B4uMai6fNB80k0IiMYmvb2A63VrajQB4GU54COQJOPbi5zTAWK13R4yLSqJznR0QEppGxldfpLWA5UPWzUqgzBa6BUJgNmrkjHlSRe47cFedzrAD-_mr3rVAjZRkzdYVfyUsVGMvm9-fvI4a_l73opAJZOPhrZqxnMG7BrjgVhQrndeZlnPopfPQ4Hilp6RzBg=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-12T19:45:00.000Z", "utc_arrival": "2023-05-12T17:45:00.000Z", "local_departure": "2023-05-12T16:15:00.000Z", "utc_departure": "2023-05-12T14:15:00.000Z"}, {"id": "0b770a224bec0000d03c291b_0|0a220b774bef00006c5bf15f_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 813.015052, "distance": 1975.87, "duration": {"departure": 12000, "return": 11700, "total": 23700}, "price": 252002.8634, "conversion": {"EUR": 659.682102, "HUF": 252002.8634}, "fare": {"adults": 126001.43, "children": 126001.43, "infants": 126001.43}, "bags_price": {"1": 95.004, "2": 190.022}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 6}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224bec0000d03c291b_0", "combination_id": "0b770a224bec0000d03c291b", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IJREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-03-20T08:20:00.000Z", "utc_arrival": "2023-03-20T07:20:00.000Z", "local_departure": "2023-03-20T05:00:00.000Z", "utc_departure": "2023-03-20T04:00:00.000Z"}, {"id": "0a220b774bef00006c5bf15f_0", "combination_id": "0a220b774bef00006c5bf15f", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6709, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-03-23T09:55:00.000Z", "utc_arrival": "2023-03-23T08:55:00.000Z", "local_departure": "2023-03-23T06:40:00.000Z", "utc_departure": "2023-03-23T05:40:00.000Z"}], "booking_token": "EE-pCh9CBdEW-r2xVG592kiBZeC5cQhdXmilLKVSEtn_-xD4FDF3nIC3Y3ldby1ORLNrHqIbGuLnIsj4T7iVJvkoHYKCtLOmDyGPBx9FkfNfTwSAT9sKaM0ljta6hgBYtyQuUKnDTKUiSxrGtDSZgfqNrVmwtokT55aTu1aX6PnmubzRKLkhFwk0WLx1SCmNr2spPaaJcJ-hfjk7twNzjyubkLQ-0WZh2289_meQI5hEGSWht9JSmSntioVUeETpxLkKZO4xCo5E204PxPfuF1XH2nd_7pjxy5BnFKjnO40e0UnSeEc2099If_nzLIN0Y-QNwGWhKXSEzpG55Y4JbUX1ucDLVrWy0IE8e7IFe6ixZMm4OqbKF56Sh9gbuZ9mAiq8SW-jIekbuFXB7Gs5w0NGGGSW6yijcta0i9nbTtvzdy9iIkuqq95KJ3b-szG9kUmK2kDnRLixDUYW0Cy-1vSktr0tDNt5bwnqyAITdvWfvrpVzY9VUZK3ecNb2QHgxcCc_Y-VWg9PtFCQpdeNzNsfZicM4hUaDg2yGbpVWxPPo97h-jDWCey3fy8Con3XkxMwo9QtiZsOECod7cNpYp0ovfYCqg7J_TbgP3bm3hjuITavF2GrMoTTxVMFywjzaVagEvqSlDHZ5wKOqTant72InLbFRuSceG-I6koptyaLSbLtBO-RMp2muDC2IydmSb1npW75wX6C0Uh-YPAPVF8yggITY2LSD2bL-WLDNJG0ERFl46_7dcbQtNwYQ17PS_G0wCnzx3QwIFWSUjrwQM_hJFwdQYSiisbDc3snU7xE=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224bec0000d03c291b_0%7C0a220b774bef00006c5bf15f_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EE-pCh9CBdEW-r2xVG592kiBZeC5cQhdXmilLKVSEtn_-xD4FDF3nIC3Y3ldby1ORLNrHqIbGuLnIsj4T7iVJvkoHYKCtLOmDyGPBx9FkfNfTwSAT9sKaM0ljta6hgBYtyQuUKnDTKUiSxrGtDSZgfqNrVmwtokT55aTu1aX6PnmubzRKLkhFwk0WLx1SCmNr2spPaaJcJ-hfjk7twNzjyubkLQ-0WZh2289_meQI5hEGSWht9JSmSntioVUeETpxLkKZO4xCo5E204PxPfuF1XH2nd_7pjxy5BnFKjnO40e0UnSeEc2099If_nzLIN0Y-QNwGWhKXSEzpG55Y4JbUX1ucDLVrWy0IE8e7IFe6ixZMm4OqbKF56Sh9gbuZ9mAiq8SW-jIekbuFXB7Gs5w0NGGGSW6yijcta0i9nbTtvzdy9iIkuqq95KJ3b-szG9kUmK2kDnRLixDUYW0Cy-1vSktr0tDNt5bwnqyAITdvWfvrpVzY9VUZK3ecNb2QHgxcCc_Y-VWg9PtFCQpdeNzNsfZicM4hUaDg2yGbpVWxPPo97h-jDWCey3fy8Con3XkxMwo9QtiZsOECod7cNpYp0ovfYCqg7J_TbgP3bm3hjuITavF2GrMoTTxVMFywjzaVagEvqSlDHZ5wKOqTant72InLbFRuSceG-I6koptyaLSbLtBO-RMp2muDC2IydmSb1npW75wX6C0Uh-YPAPVF8yggITY2LSD2bL-WLDNJG0ERFl46_7dcbQtNwYQ17PS_G0wCnzx3QwIFWSUjrwQM_hJFwdQYSiisbDc3snU7xE=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-03-20T08:20:00.000Z", "utc_arrival": "2023-03-20T07:20:00.000Z", "local_departure": "2023-03-20T05:00:00.000Z", "utc_departure": "2023-03-20T04:00:00.000Z"}, {"id": "0b770a224c430000a78af0de_0|0a220b774c470000d863fde0_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 816.0274, "distance": 1975.87, "duration": {"departure": 12600, "return": 11400, "total": 24000}, "price": 252644.2593, "conversion": {"EUR": 661.36112, "HUF": 252644.2593}, "fare": {"adults": 126322.13, "children": 126322.13, "infants": 126322.13}, "bags_price": {"1": 72.268, "2": 154.336}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 158, "hold_height": 52, "hold_length": 78, "hold_weight": 20, "hold_width": 28, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 3, "personal_item_width": 15}, "availability": {"seats": 2}, "airlines": ["W6", "IB"], "route": [{"id": "0b770a224c430000a78af0de_0", "combination_id": "0b770a224c430000a78af0de", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IJREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-15T21:15:00.000Z", "utc_arrival": "2023-06-15T19:15:00.000Z", "local_departure": "2023-06-15T17:45:00.000Z", "utc_departure": "2023-06-15T15:45:00.000Z"}, {"id": "0a220b774c470000d863fde0_0", "combination_id": "0a220b774c470000d863fde0", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "IB", "flight_no": 3278, "operating_carrier": "IB", "operating_flight_no": "3278", "fare_basis": "SWNNAOB4", "fare_category": "M", "fare_classes": "S", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-19T14:55:00.000Z", "utc_arrival": "2023-06-19T12:55:00.000Z", "local_departure": "2023-06-19T11:45:00.000Z", "utc_departure": "2023-06-19T09:45:00.000Z"}], "booking_token": "Egh-qFlL-QBKWKIOjl_aQLXX3SMZxivblqeQUctpCSYHSS-2j7xbyBPUiGgdBCUv1wo4XwjgyiCVJIJbpniH041-1F9TNkK-JzUHRQ6aMpODRc3eQWu_mg0ZL2vZvLFcuLfmPf6CjX4NL5RlfmtVgPOKDxZY6ar4PDOlmwBpISDNykiEkcl7H4mCIZYny1vQDqASAz72rzf8vE7UwxG9U7bjSRJTTbs4Jehq2ybQmblXG-KjcuIDlnI4RyTM59Gin2jh5frErrz0CNB_5LbapgTGYa6I0PH_dPMtsYExutdlBTcsu3SCrvkyqrhkyLqfhUyzXPKrhVyli7mhjQwaSFXWc5D_ny3a1JwxkN9SnSAnuriRkuLd0zrkIdsv42KbJYuqw96K0NA89-07lhtrcLmcbfjqahWYV7MoN7ECaOV5ew_2lxYvVMG1i3YQLt3LdVcq42AnkLYZf-hkqxXG2DFhgVGlxdbzYuRdg5i-NKMuNknM18V3yu0cusD9ybYgQTqm1pIXpAfjTSE1iQZnbb6tbetsah7okc0MoJIGBgFTC9vT08eko3EeYGwbaRUCiemhceSGHjlaO0MkTj1PwRZQe96r3jKzRMpiin5CVMkI9aV5NPImKeBLkYMjEJpXbe9TXfndaNHQL7zdqWYgVlOjqLh2QMvtjtfh1tN4MN3Al8cDnvisoJ_8OxCj5PdNbWgZbnVVTvdArPEiuCcCHpb6-jl347ohATNXxfhcBNyU7DnfXHNEtmHbhGtU1bHhO5Is62Djok_lDWZ83wahaiRv5sQcVO8VzrVwqTy6iahc=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c430000a78af0de_0%7C0a220b774c470000d863fde0_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=Egh-qFlL-QBKWKIOjl_aQLXX3SMZxivblqeQUctpCSYHSS-2j7xbyBPUiGgdBCUv1wo4XwjgyiCVJIJbpniH041-1F9TNkK-JzUHRQ6aMpODRc3eQWu_mg0ZL2vZvLFcuLfmPf6CjX4NL5RlfmtVgPOKDxZY6ar4PDOlmwBpISDNykiEkcl7H4mCIZYny1vQDqASAz72rzf8vE7UwxG9U7bjSRJTTbs4Jehq2ybQmblXG-KjcuIDlnI4RyTM59Gin2jh5frErrz0CNB_5LbapgTGYa6I0PH_dPMtsYExutdlBTcsu3SCrvkyqrhkyLqfhUyzXPKrhVyli7mhjQwaSFXWc5D_ny3a1JwxkN9SnSAnuriRkuLd0zrkIdsv42KbJYuqw96K0NA89-07lhtrcLmcbfjqahWYV7MoN7ECaOV5ew_2lxYvVMG1i3YQLt3LdVcq42AnkLYZf-hkqxXG2DFhgVGlxdbzYuRdg5i-NKMuNknM18V3yu0cusD9ybYgQTqm1pIXpAfjTSE1iQZnbb6tbetsah7okc0MoJIGBgFTC9vT08eko3EeYGwbaRUCiemhceSGHjlaO0MkTj1PwRZQe96r3jKzRMpiin5CVMkI9aV5NPImKeBLkYMjEJpXbe9TXfndaNHQL7zdqWYgVlOjqLh2QMvtjtfh1tN4MN3Al8cDnvisoJ_8OxCj5PdNbWgZbnVVTvdArPEiuCcCHpb6-jl347ohATNXxfhcBNyU7DnfXHNEtmHbhGtU1bHhO5Is62Djok_lDWZ83wahaiRv5sQcVO8VzrVwqTy6iahc=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-15T21:15:00.000Z", "utc_arrival": "2023-06-15T19:15:00.000Z", "local_departure": "2023-06-15T17:45:00.000Z", "utc_departure": "2023-06-15T15:45:00.000Z"}, {"id": "0b770a224bfa0000e3b3cbb8_0|0a220b774bfe0000f8408ba8_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 820.57176, "distance": 1975.87, "duration": {"departure": 12000, "return": 12900, "total": 24900}, "price": 252852.2121, "conversion": {"EUR": 661.90549, "HUF": 252852.2121}, "fare": {"adults": 126426.11, "children": 126426.11, "infants": 126426.11}, "bags_price": {"1": 110.404, "2": 193.704}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 2}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224bfa0000e3b3cbb8_0", "combination_id": "0b770a224bfa0000e3b3cbb8", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-03T14:00:00.000Z", "utc_arrival": "2023-04-03T12:00:00.000Z", "local_departure": "2023-04-03T10:40:00.000Z", "utc_departure": "2023-04-03T08:40:00.000Z"}, {"id": "0a220b774bfe0000f8408ba8_0", "combination_id": "0a220b774bfe0000f8408ba8", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "JKREG", "fare_category": "M", "fare_classes": "J", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-08T00:05:00.000Z", "utc_arrival": "2023-04-07T22:05:00.000Z", "local_departure": "2023-04-07T20:30:00.000Z", "utc_departure": "2023-04-07T18:30:00.000Z"}], "booking_token": "EpzVzUdwZcLF1yn2OUNI39X7ef0hBY5ig1fuvB50LRaaKK9AM_ad9kuEntSxxL8hGTv0tX2j4iZ7QgdSrncrPBhF7EtKcyDoNHHjG6ftobC-pyhN_aghCRTELItCIR3U01mRt6ud8BpzkkP3xkQyb8TMBAUUM3JF7XVAoCC_oHeZBHgcBMwChvsn33xIajDyTvjsekieA42IFgeu7Cexv54N_GfA2uT7q66fvYCv-k7zlQcOdBuqBF3VpnnRtHEUTzTeScv4pMLFsHAHljE7oLNBsrQYTLKY_5nv--t4Ke1ID_oX4JbaVdFVfFEibCAeIPC_5zoLq5EXsoh_0fpoty1iIYKQeFknrfwJOYtXvMoJD-pSWwPZRBphVYkKD1YFC_tAE8abTDy-SF3HdDPmNTwuUnvAy6F_mMYthP5iatyqfBeDAUFyv2K3raEC2-gbCgQghUr763wtuJluvhqEDXCJrdPV_PtMX_FUK0ymj9ewCfYL9ZDw7kH_-xDpc3h7N9R9FC20Jc2l0o_Yp-K_17Tc49nhinZEsuxEDgVMLCjGv1DPLRghG4SmHpY9mQlQGyG39eaoOzCcGgh7zUoIdyrnIQbZNNfKUncuYLCoQfOWKNmBo5gBmbtYkXa09IK9-2jRjypgoM9zaXJiVXwll8KZj_NX42EdWgm-D29Hl8v-1IKyVisE8ccDhHdZ24hoO1Ik8CpFoekcG8xz2tLqlvZF67iaqGzgs3QDGdTP-J0b0ekcoRFJq4riTBDJMRFOC", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224bfa0000e3b3cbb8_0%7C0a220b774bfe0000f8408ba8_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EpzVzUdwZcLF1yn2OUNI39X7ef0hBY5ig1fuvB50LRaaKK9AM_ad9kuEntSxxL8hGTv0tX2j4iZ7QgdSrncrPBhF7EtKcyDoNHHjG6ftobC-pyhN_aghCRTELItCIR3U01mRt6ud8BpzkkP3xkQyb8TMBAUUM3JF7XVAoCC_oHeZBHgcBMwChvsn33xIajDyTvjsekieA42IFgeu7Cexv54N_GfA2uT7q66fvYCv-k7zlQcOdBuqBF3VpnnRtHEUTzTeScv4pMLFsHAHljE7oLNBsrQYTLKY_5nv--t4Ke1ID_oX4JbaVdFVfFEibCAeIPC_5zoLq5EXsoh_0fpoty1iIYKQeFknrfwJOYtXvMoJD-pSWwPZRBphVYkKD1YFC_tAE8abTDy-SF3HdDPmNTwuUnvAy6F_mMYthP5iatyqfBeDAUFyv2K3raEC2-gbCgQghUr763wtuJluvhqEDXCJrdPV_PtMX_FUK0ymj9ewCfYL9ZDw7kH_-xDpc3h7N9R9FC20Jc2l0o_Yp-K_17Tc49nhinZEsuxEDgVMLCjGv1DPLRghG4SmHpY9mQlQGyG39eaoOzCcGgh7zUoIdyrnIQbZNNfKUncuYLCoQfOWKNmBo5gBmbtYkXa09IK9-2jRjypgoM9zaXJiVXwll8KZj_NX42EdWgm-D29Hl8v-1IKyVisE8ccDhHdZ24hoO1Ik8CpFoekcG8xz2tLqlvZF67iaqGzgs3QDGdTP-J0b0ekcoRFJq4riTBDJMRFOC", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-04-03T14:00:00.000Z", "utc_arrival": "2023-04-03T12:00:00.000Z", "local_departure": "2023-04-03T10:40:00.000Z", "utc_departure": "2023-04-03T08:40:00.000Z"}, {"id": "0b770a224c15000010364d2a_0|0a220b774c180000c0e5a290_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 817.399493, "distance": 1975.87, "duration": {"departure": 12600, "return": 11400, "total": 24000}, "price": 253168.4077, "conversion": {"EUR": 662.733213, "HUF": 253168.4077}, "fare": {"adults": 126584.2, "children": 126584.2, "infants": 126584.2}, "bags_price": {"1": 104.524, "2": 218.834}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 158, "hold_height": 52, "hold_length": 78, "hold_weight": 20, "hold_width": 28, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 3, "personal_item_width": 15}, "availability": {"seats": 3}, "airlines": ["W6", "IB"], "route": [{"id": "0b770a224c15000010364d2a_0", "combination_id": "0b770a224c15000010364d2a", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "KLREG", "fare_category": "M", "fare_classes": "K", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-30T17:05:00.000Z", "utc_arrival": "2023-04-30T15:05:00.000Z", "local_departure": "2023-04-30T13:35:00.000Z", "utc_departure": "2023-04-30T11:35:00.000Z"}, {"id": "0a220b774c180000c0e5a290_0", "combination_id": "0a220b774c180000c0e5a290", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "IB", "flight_no": 3278, "operating_carrier": "IB", "operating_flight_no": "3278", "fare_basis": "VZNNAOB4", "fare_category": "M", "fare_classes": "V", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-03T14:55:00.000Z", "utc_arrival": "2023-05-03T12:55:00.000Z", "local_departure": "2023-05-03T11:45:00.000Z", "utc_departure": "2023-05-03T09:45:00.000Z"}], "booking_token": "EkLopwMjXBfByCoZ3L6_pvPDxNEOsMakqABaw1ZIathxAsl83W9l0G7GeHz6tMPBudX78tyWtbvFqhYLDBRSz9La_fXOYiDNsDmFev6m_Sgwel06Qsihu-yTWCmPuVDOIkjC6suj7WxddzbcjWHvFMwcGEKoTm0DnZp1ApKSAPVTjHKQC8gBGawMG8WOACEKpLW-oRYZXt2uuPWzFPwOziRMlmLez3CiViv9ohkThQb17v7DqDprcf00Z4ACAlCN_t_LTsiEBLWZJEeNueeXEucnVNduIq6ziBfsN2npdV69LRsTkvRgQlRVK2cEImSe1aLJkFHNF-BSzgrjxlad7mk8AgCICSCYvVkDYMEL6rxNxzhWDxrZl4itIT0XeXN9pvRUdrOLU25hSWL-YhVhWrQ3o_4zOeW4_xCw4zjDyMuhEAfl27n6E0f-zmShlDoQi_12YPQboLZ-UipO3E1fPOryjMM1ibI5ZEmesPoJl_bFuWD1W6cN_o0UUIjnoKp6_DOcPUaTYlD2fR_yVSElTh9mS5aEzOL78sQw0ndWZ2rDONEnPn7hHQ8IfkjCScnY22QgzbUqQdgczydlCwmpldaOYhzGlJPwacoErOej84aIrHIW9wdUeHqRyBSNol19moPOI4o4TsHoB_C9M6BwQOWGL8SvnRjPhGb_AlpJQfp6lT7hJ-YtmsgF34QYep_yCvNB92Zolmp9j6ewEOGQ_sqO5P46HLCMA3utcPzkuN3r6W_x1WZQSDEe06rSOWr1f6dT62RAQVxQtCqIAnmZVXzt-OZjti0N666z9hH3BB4Uj2uA8Y5aU2qfYHGsYI_XY", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c15000010364d2a_0%7C0a220b774c180000c0e5a290_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EkLopwMjXBfByCoZ3L6_pvPDxNEOsMakqABaw1ZIathxAsl83W9l0G7GeHz6tMPBudX78tyWtbvFqhYLDBRSz9La_fXOYiDNsDmFev6m_Sgwel06Qsihu-yTWCmPuVDOIkjC6suj7WxddzbcjWHvFMwcGEKoTm0DnZp1ApKSAPVTjHKQC8gBGawMG8WOACEKpLW-oRYZXt2uuPWzFPwOziRMlmLez3CiViv9ohkThQb17v7DqDprcf00Z4ACAlCN_t_LTsiEBLWZJEeNueeXEucnVNduIq6ziBfsN2npdV69LRsTkvRgQlRVK2cEImSe1aLJkFHNF-BSzgrjxlad7mk8AgCICSCYvVkDYMEL6rxNxzhWDxrZl4itIT0XeXN9pvRUdrOLU25hSWL-YhVhWrQ3o_4zOeW4_xCw4zjDyMuhEAfl27n6E0f-zmShlDoQi_12YPQboLZ-UipO3E1fPOryjMM1ibI5ZEmesPoJl_bFuWD1W6cN_o0UUIjnoKp6_DOcPUaTYlD2fR_yVSElTh9mS5aEzOL78sQw0ndWZ2rDONEnPn7hHQ8IfkjCScnY22QgzbUqQdgczydlCwmpldaOYhzGlJPwacoErOej84aIrHIW9wdUeHqRyBSNol19moPOI4o4TsHoB_C9M6BwQOWGL8SvnRjPhGb_AlpJQfp6lT7hJ-YtmsgF34QYep_yCvNB92Zolmp9j6ewEOGQ_sqO5P46HLCMA3utcPzkuN3r6W_x1WZQSDEe06rSOWr1f6dT62RAQVxQtCqIAnmZVXzt-OZjti0N666z9hH3BB4Uj2uA8Y5aU2qfYHGsYI_XY", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-04-30T17:05:00.000Z", "utc_arrival": "2023-04-30T15:05:00.000Z", "local_departure": "2023-04-30T13:35:00.000Z", "utc_departure": "2023-04-30T11:35:00.000Z"}, {"id": "0b770a224c210000fa6546ee_0|0a220b774c2400009a975815_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 820.906697, "distance": 1975.87, "duration": {"departure": 12600, "return": 11400, "total": 24000}, "price": 254508.1825, "conversion": {"EUR": 666.240417, "HUF": 254508.1825}, "fare": {"adults": 127254.09, "children": 127254.09, "infants": 127254.09}, "bags_price": {"1": 81.942, "2": 163.898}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 4}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224c210000fa6546ee_0", "combination_id": "0b770a224c210000fa6546ee", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "GFREG", "fare_category": "M", "fare_classes": "G", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-12T19:45:00.000Z", "utc_arrival": "2023-05-12T17:45:00.000Z", "local_departure": "2023-05-12T16:15:00.000Z", "utc_departure": "2023-05-12T14:15:00.000Z"}, {"id": "0a220b774c2400009a975815_0", "combination_id": "0a220b774c2400009a975815", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-15T10:15:00.000Z", "utc_arrival": "2023-05-15T08:15:00.000Z", "local_departure": "2023-05-15T07:05:00.000Z", "utc_departure": "2023-05-15T05:05:00.000Z"}], "booking_token": "EY6-iVFUEVgybE6tn9o-eJJJuSE0lPzkqCfiyICRngQAHjq1wTBYIg7XaW3_qfL0mwodKoMSaJfEPfVt2bNDgFeANFGhoK9pn7h5Rc1xw4HbaxtqhhtOu6jrQk5B7379f91D8igOL8ORzoI2_00aCuodnRTWRDUoeJL8QigaucZ9huR8qJfkQDZqaNxs1pB-0PeUIvZD2PoRNW_aDBiyf-Rn2QHOK89ZEDtjI8FRPyW1INK1J3DupBbq6vG6i10EREasq1UeHGU4drrwzNbcmE30nEKzTbMWdscqSX0TpwFsf1JtlDkU8ALk9q4mhwwmW-FDyWX5f7eOEwkkO5ABIOwO-Tk7oBPKB5NmChERB-DwWZIOK7isEVSrJSP4eevBu0799WQh49sTXMvMMV-_iVxmN9rWGRUM7r14i3wSH-3y7Ad5TihlEdypqSpYlloa6Cr_VtRoLS91Fi8idjrkXNY2ldmM-S_pf3rlYfabXDDGtDdhk00cVNS6NQZlaiNXs8IrQZxCBnNRgWvtM0IcBBCV0q14B5M46dpfTr3106svesHlWdx3DDjzPPJn1O0GyhKG6W4-kXVIPqOyh70W_qrtTFht7LGzcdioVn2ii_MVmaXIskOzzZAthGScPjq4DOHRBgT0NdnOEcwfWLHDHFhKxu2D_iXfcVyiM7JTYSrcVnfGxyuMXF10LwQC8x52sBOAwuDhe8C_ac4Uo24qhnpmBSezkESRo5WTfuu-pw1odcFwGEJuH6ZtwmJGpwNQObkthKndrj_DAMwB0R63Qjbp498Xd7R_DHGDvRdpDwxI=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c210000fa6546ee_0%7C0a220b774c2400009a975815_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EY6-iVFUEVgybE6tn9o-eJJJuSE0lPzkqCfiyICRngQAHjq1wTBYIg7XaW3_qfL0mwodKoMSaJfEPfVt2bNDgFeANFGhoK9pn7h5Rc1xw4HbaxtqhhtOu6jrQk5B7379f91D8igOL8ORzoI2_00aCuodnRTWRDUoeJL8QigaucZ9huR8qJfkQDZqaNxs1pB-0PeUIvZD2PoRNW_aDBiyf-Rn2QHOK89ZEDtjI8FRPyW1INK1J3DupBbq6vG6i10EREasq1UeHGU4drrwzNbcmE30nEKzTbMWdscqSX0TpwFsf1JtlDkU8ALk9q4mhwwmW-FDyWX5f7eOEwkkO5ABIOwO-Tk7oBPKB5NmChERB-DwWZIOK7isEVSrJSP4eevBu0799WQh49sTXMvMMV-_iVxmN9rWGRUM7r14i3wSH-3y7Ad5TihlEdypqSpYlloa6Cr_VtRoLS91Fi8idjrkXNY2ldmM-S_pf3rlYfabXDDGtDdhk00cVNS6NQZlaiNXs8IrQZxCBnNRgWvtM0IcBBCV0q14B5M46dpfTr3106svesHlWdx3DDjzPPJn1O0GyhKG6W4-kXVIPqOyh70W_qrtTFht7LGzcdioVn2ii_MVmaXIskOzzZAthGScPjq4DOHRBgT0NdnOEcwfWLHDHFhKxu2D_iXfcVyiM7JTYSrcVnfGxyuMXF10LwQC8x52sBOAwuDhe8C_ac4Uo24qhnpmBSezkESRo5WTfuu-pw1odcFwGEJuH6ZtwmJGpwNQObkthKndrj_DAMwB0R63Qjbp498Xd7R_DHGDvRdpDwxI=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-12T19:45:00.000Z", "utc_arrival": "2023-05-12T17:45:00.000Z", "local_departure": "2023-05-12T16:15:00.000Z", "utc_departure": "2023-05-12T14:15:00.000Z"}, {"id": "0b770a224c4a00006b86e63f_0|0a220b774c4d0000e5d40dae_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 822.339406, "distance": 1975.87, "duration": {"departure": 12600, "return": 11700, "total": 24300}, "price": 254546.1459, "conversion": {"EUR": 666.339796, "HUF": 254546.1459}, "fare": {"adults": 127273.07, "children": 130571.74, "infants": 130571.74}, "bags_price": {"1": 123.242, "2": 246.47}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 439, "hold_height": 149, "hold_length": 171, "hold_weight": 20, "hold_width": 119, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 4}, "airlines": ["W6"], "route": [{"id": "0b770a224c4a00006b86e63f_0", "combination_id": "0b770a224c4a00006b86e63f", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "HREG", "fare_category": "M", "fare_classes": "H", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-22T21:15:00.000Z", "utc_arrival": "2023-06-22T19:15:00.000Z", "local_departure": "2023-06-22T17:45:00.000Z", "utc_departure": "2023-06-22T15:45:00.000Z"}, {"id": "0a220b774c4d0000e5d40dae_0", "combination_id": "0a220b774c4d0000e5d40dae", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-25T21:05:00.000Z", "utc_arrival": "2023-06-25T19:05:00.000Z", "local_departure": "2023-06-25T17:50:00.000Z", "utc_departure": "2023-06-25T15:50:00.000Z"}], "booking_token": "EufJAhA1uMkr0FEXT_j_N8sX6IYg2JhNBSQyz4I22fEXXdWzoA5FkqZQyRAAIiFk3XbhjYCiwiXPpnztrgO5q4tkDWB7E2bPLNrFhHAAokIl5IIX2BLHOeQ3WFMr-Vn-7B6MnTZ4BvzeRzId4BJueZktbQ1XuLTbBsAzaYhX53dpqsp2Uha1UibEEsflbne5pPgz6bSKVXAvAFnVzy2xJZ-X297QZjVK4y1iq0rrT3Rm5oBslPuyQO4007vfYZIkKGQqd5IW0FFwetXX0cT8wkx2Ejh44cPkxIFQGcWG8Ynv8rknkV-sBEvWETtqdor5s2UdaNKp-LCmy1ZXvwLffQuluCRQcbO1s9KLNgEd09SPgX_Me4zatoHwWjHA9h8mYRA5yZmMPHGWL-2zO9E782D88-ciGIL4oUs4wc93Fi4W6OdezUB6UMa9OPnITIy9SzamxUIkQRaStfidQZqWCLQZKebMSRhIkDko_TpaSFYYLcZdiS-PSWbYOgkiEVjCVhQwCrdNnndDXalS3jf2K42fmbmK9OTc2vJ_bqfVRn-gbQz9w0oGmsbr8eiuh4FuInFnSlTUNZCAiy5nr3JUp8fWGRGjwxWOmWw25xpp1-QSSKi1dyZ97CPVajPM1cCZt3v4VGWcG599CQTLHBGLsqc5O462TBQm4_nxv_obc_4yiv7Qyz8UHiXi3iBxFEJw3z0A9TZQqGbh5K-GkSDgvubFouhVv1RA6YaoRrBO28aiaI5DAdZF9YsuEshEHEl_Vumn2f5ILSz006YPsPmRcIwfi2yGZKSFEFsaTSpcqvjc=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c4a00006b86e63f_0%7C0a220b774c4d0000e5d40dae_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EufJAhA1uMkr0FEXT_j_N8sX6IYg2JhNBSQyz4I22fEXXdWzoA5FkqZQyRAAIiFk3XbhjYCiwiXPpnztrgO5q4tkDWB7E2bPLNrFhHAAokIl5IIX2BLHOeQ3WFMr-Vn-7B6MnTZ4BvzeRzId4BJueZktbQ1XuLTbBsAzaYhX53dpqsp2Uha1UibEEsflbne5pPgz6bSKVXAvAFnVzy2xJZ-X297QZjVK4y1iq0rrT3Rm5oBslPuyQO4007vfYZIkKGQqd5IW0FFwetXX0cT8wkx2Ejh44cPkxIFQGcWG8Ynv8rknkV-sBEvWETtqdor5s2UdaNKp-LCmy1ZXvwLffQuluCRQcbO1s9KLNgEd09SPgX_Me4zatoHwWjHA9h8mYRA5yZmMPHGWL-2zO9E782D88-ciGIL4oUs4wc93Fi4W6OdezUB6UMa9OPnITIy9SzamxUIkQRaStfidQZqWCLQZKebMSRhIkDko_TpaSFYYLcZdiS-PSWbYOgkiEVjCVhQwCrdNnndDXalS3jf2K42fmbmK9OTc2vJ_bqfVRn-gbQz9w0oGmsbr8eiuh4FuInFnSlTUNZCAiy5nr3JUp8fWGRGjwxWOmWw25xpp1-QSSKi1dyZ97CPVajPM1cCZt3v4VGWcG599CQTLHBGLsqc5O462TBQm4_nxv_obc_4yiv7Qyz8UHiXi3iBxFEJw3z0A9TZQqGbh5K-GkSDgvubFouhVv1RA6YaoRrBO28aiaI5DAdZF9YsuEshEHEl_Vumn2f5ILSz006YPsPmRcIwfi2yGZKSFEFsaTSpcqvjc=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-22T21:15:00.000Z", "utc_arrival": "2023-06-22T19:15:00.000Z", "local_departure": "2023-06-22T17:45:00.000Z", "utc_departure": "2023-06-22T15:45:00.000Z"}, {"id": "0b770a224c09000063e5c3d1_0|0a220b774c0c00003f9c62a9_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 820.950547, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 255543.615, "conversion": {"EUR": 668.950927, "HUF": 255543.615}, "fare": {"adults": 127771.81, "children": 127771.81, "infants": 127771.81}, "bags_price": {"1": 74.508, "2": 149.016}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 6}, "airlines": ["FR"], "route": [{"id": "0b770a224c09000063e5c3d1_0", "combination_id": "0b770a224c09000063e5c3d1", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-18T10:15:00.000Z", "utc_arrival": "2023-04-18T08:15:00.000Z", "local_departure": "2023-04-18T06:55:00.000Z", "utc_departure": "2023-04-18T04:55:00.000Z"}, {"id": "0a220b774c0c00003f9c62a9_0", "combination_id": "0a220b774c0c00003f9c62a9", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-21T18:00:00.000Z", "utc_arrival": "2023-04-21T16:00:00.000Z", "local_departure": "2023-04-21T14:50:00.000Z", "utc_departure": "2023-04-21T12:50:00.000Z"}], "booking_token": "EfUb4nE4fncpsnuFKkMxXyYL-w07O6s5Q9QeOww32XzOxk7YmLk3xk0vw5FXjQTTn2LhWWMvoraTgTKq5eRkPwUK02x9uEkdvxO0Jp32wtFYTaJmvnnoIgrA26W337bfPdQNr0IdjybUG-vdS4sgeuKttRvthl8-vvL2lE4ecr5wWhKJB_O430w56sAQOuV8uecjDUyDpJtZ3CA86H1sVib3sUwfLvP78I7VhL7WXM8Z361fXovrC7TpWfJnzmgMZMA_ShUZZZ66Snmzi2bG7UFbdqeAdpnBH9rucKUVYcXXNWSdt6iJdeE21atEU1u6mG3WNrbkweQuWH8LJJ3zG7uqbAmVFQbHrEsscWltb1zg4EGN1LZHTMxbj5z-SAUUCD6kNwiJewaKYj3LogngR2h0jM6mgyR7O25-nvqpxP1iIopesuJr10kIaYiQO5QJS6c6PQzcGfDzvc9jLR1-oXnuK7OE7ZldyAHMhRWmFAcW5XAHh2nUK8ay9HTQtr39eUO5WRYWIP-g-t3MlPrYxSkS6cEKyaF0aYe-ZGCrU8IexqOOpXiIE-MX-tNq1QQ4_LIWcDzDunpg9qvFKlXtMd1C3UtD24yWK0lc8seKM5zRSae3nz-qGU4n2kIXWbTjLyYJJFcZb_NZp1MuGktBxd9o6fKJokhEoj_ekK7ENB29rTb9CuYmeZ0sYDn2UB9BHf3ol7_Jqmmpoz_7AG_zpcg==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c09000063e5c3d1_0%7C0a220b774c0c00003f9c62a9_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EfUb4nE4fncpsnuFKkMxXyYL-w07O6s5Q9QeOww32XzOxk7YmLk3xk0vw5FXjQTTn2LhWWMvoraTgTKq5eRkPwUK02x9uEkdvxO0Jp32wtFYTaJmvnnoIgrA26W337bfPdQNr0IdjybUG-vdS4sgeuKttRvthl8-vvL2lE4ecr5wWhKJB_O430w56sAQOuV8uecjDUyDpJtZ3CA86H1sVib3sUwfLvP78I7VhL7WXM8Z361fXovrC7TpWfJnzmgMZMA_ShUZZZ66Snmzi2bG7UFbdqeAdpnBH9rucKUVYcXXNWSdt6iJdeE21atEU1u6mG3WNrbkweQuWH8LJJ3zG7uqbAmVFQbHrEsscWltb1zg4EGN1LZHTMxbj5z-SAUUCD6kNwiJewaKYj3LogngR2h0jM6mgyR7O25-nvqpxP1iIopesuJr10kIaYiQO5QJS6c6PQzcGfDzvc9jLR1-oXnuK7OE7ZldyAHMhRWmFAcW5XAHh2nUK8ay9HTQtr39eUO5WRYWIP-g-t3MlPrYxSkS6cEKyaF0aYe-ZGCrU8IexqOOpXiIE-MX-tNq1QQ4_LIWcDzDunpg9qvFKlXtMd1C3UtD24yWK0lc8seKM5zRSae3nz-qGU4n2kIXWbTjLyYJJFcZb_NZp1MuGktBxd9o6fKJokhEoj_ekK7ENB29rTb9CuYmeZ0sYDn2UB9BHf3ol7_Jqmmpoz_7AG_zpcg==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-04-18T10:15:00.000Z", "utc_arrival": "2023-04-18T08:15:00.000Z", "local_departure": "2023-04-18T06:55:00.000Z", "utc_departure": "2023-04-18T04:55:00.000Z"}, {"id": "0b770a224c2000007c0ce671_0|0a220b774c2400009a975815_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 823.859008, "distance": 1975.87, "duration": {"departure": 12600, "return": 11400, "total": 24000}, "price": 255635.9846, "conversion": {"EUR": 669.192728, "HUF": 255635.9846}, "fare": {"adults": 127817.99, "children": 130801.52, "infants": 130801.52}, "bags_price": {"1": 84.7, "2": 169.386}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 4}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224c2000007c0ce671_0", "combination_id": "0b770a224c2000007c0ce671", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "GFREG", "fare_category": "M", "fare_classes": "G", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-11T21:15:00.000Z", "utc_arrival": "2023-05-11T19:15:00.000Z", "local_departure": "2023-05-11T17:45:00.000Z", "utc_departure": "2023-05-11T15:45:00.000Z"}, {"id": "0a220b774c2400009a975815_0", "combination_id": "0a220b774c2400009a975815", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-15T10:15:00.000Z", "utc_arrival": "2023-05-15T08:15:00.000Z", "local_departure": "2023-05-15T07:05:00.000Z", "utc_departure": "2023-05-15T05:05:00.000Z"}], "booking_token": "EAa5IwdGH3GdfTdX6w3LLrwdiR4XETiuyfkmuB3czu84XIbFwdBmwEGA0Fkmfj9qVQNgAmVlTpZpC-SJjPs19pT67acbp0WxkseFzXJWy8F8w7fCqf6M6-zRhSpyd76F72XHmR-yEZc1XGHiPvG8YkaSPa4w8gZJeDZSj_y2BmbQguXAJ_bxBW4iYxgkqKjUYAjj5IH8JzfNFd1XITYiE0yofolzbwuTU0_z-S47oJRAnnbsTPk90Awj90yq7gwLWBXrgsQxqq7Fj1ToJXBBp6DPg19od9CyD52X18iEeqzga-92ZjQI7buqrcPl_35HR5hDXRy2EMkUuAx79cFwUqWQgKEfidlUUvSJGb5torz7e2DnNg4vxe_WvMJcDHlxEDsKMyKChIjIh4Bi22M4P3dIev4FKNpRW1hSEOjjXt1JdN-tVHLi9RG2pLPssFMAUBYI-nBpBNOyO82XKN9RHNW-PPObs5d-SA9_3hf6qQIIYcgzM0NNuLiKUSjR0uvbFlwWq-8fivAenzlz8s6B3nVQwYwByTar21PIyuMrTa-crHLg7qvL8agRfOy0eyJR6yUsVE_YwlgUd9h6KODadMiO1_rnQOdEkYCl73-m3VcGETZ_azx1-cl6npeHuIGXpSG9ziWkrHI2rzJG0vJN-C5WJw_C4yGOfBLeio_uA2xTIUApzu4hR3k813t_-ginKcUtU0grVzea8XUeCLksz2VmAB5hXto43CL8kdnr8CEoAOUYbdwkmqyDVYUC_55NmWVbcZmnqiimvYEBeYdCihl8OnLcasB6FJJPY0ZdvR-BomYvmUPN0c4tdxIcFJTRc", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c2000007c0ce671_0%7C0a220b774c2400009a975815_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EAa5IwdGH3GdfTdX6w3LLrwdiR4XETiuyfkmuB3czu84XIbFwdBmwEGA0Fkmfj9qVQNgAmVlTpZpC-SJjPs19pT67acbp0WxkseFzXJWy8F8w7fCqf6M6-zRhSpyd76F72XHmR-yEZc1XGHiPvG8YkaSPa4w8gZJeDZSj_y2BmbQguXAJ_bxBW4iYxgkqKjUYAjj5IH8JzfNFd1XITYiE0yofolzbwuTU0_z-S47oJRAnnbsTPk90Awj90yq7gwLWBXrgsQxqq7Fj1ToJXBBp6DPg19od9CyD52X18iEeqzga-92ZjQI7buqrcPl_35HR5hDXRy2EMkUuAx79cFwUqWQgKEfidlUUvSJGb5torz7e2DnNg4vxe_WvMJcDHlxEDsKMyKChIjIh4Bi22M4P3dIev4FKNpRW1hSEOjjXt1JdN-tVHLi9RG2pLPssFMAUBYI-nBpBNOyO82XKN9RHNW-PPObs5d-SA9_3hf6qQIIYcgzM0NNuLiKUSjR0uvbFlwWq-8fivAenzlz8s6B3nVQwYwByTar21PIyuMrTa-crHLg7qvL8agRfOy0eyJR6yUsVE_YwlgUd9h6KODadMiO1_rnQOdEkYCl73-m3VcGETZ_azx1-cl6npeHuIGXpSG9ziWkrHI2rzJG0vJN-C5WJw_C4yGOfBLeio_uA2xTIUApzu4hR3k813t_-ginKcUtU0grVzea8XUeCLksz2VmAB5hXto43CL8kdnr8CEoAOUYbdwkmqyDVYUC_55NmWVbcZmnqiimvYEBeYdCihl8OnLcasB6FJJPY0ZdvR-BomYvmUPN0c4tdxIcFJTRc", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-11T21:15:00.000Z", "utc_arrival": "2023-05-11T19:15:00.000Z", "local_departure": "2023-05-11T17:45:00.000Z", "utc_departure": "2023-05-11T15:45:00.000Z"}, {"id": "0b770a224c2000007c0ce671_0|0a220b774c23000067c13b26_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 825.485182, "distance": 1975.87, "duration": {"departure": 12600, "return": 11700, "total": 24300}, "price": 255747.8529, "conversion": {"EUR": 669.485572, "HUF": 255747.8529}, "fare": {"adults": 127873.93, "children": 130868.36, "infants": 130868.36}, "bags_price": {"1": 86.114, "2": 172.214}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 439, "hold_height": 149, "hold_length": 171, "hold_weight": 20, "hold_width": 119, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 3}, "airlines": ["W6"], "route": [{"id": "0b770a224c2000007c0ce671_0", "combination_id": "0b770a224c2000007c0ce671", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "GFREG", "fare_category": "M", "fare_classes": "G", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-11T21:15:00.000Z", "utc_arrival": "2023-05-11T19:15:00.000Z", "local_departure": "2023-05-11T17:45:00.000Z", "utc_departure": "2023-05-11T15:45:00.000Z"}, {"id": "0a220b774c23000067c13b26_0", "combination_id": "0a220b774c23000067c13b26", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IJREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-14T21:05:00.000Z", "utc_arrival": "2023-05-14T19:05:00.000Z", "local_departure": "2023-05-14T17:50:00.000Z", "utc_departure": "2023-05-14T15:50:00.000Z"}], "booking_token": "EhTAOsyifNpxqgqaZpriVefuyIGusr-WwMJc_F1VfN4M9wnBwxruDqiDM5LGecKfTht8fqTYwEDMvraa1TaMU_RXfR-0bh_r98w_UVVZdepxPNPiYVy9TXurWbQrrZ9h6RMKsE0D5wc9iDO-dIy_xanJgcZnF4OlhmgdPZL6BTBD7AMHlmzeDPInTDC4iYIIKpEh8I0QlG_qEeV95mSYQyEvLIsu1E7W-2Cpt8dldBqlB0xPXP53i39QnEMSdB_fZuFju27tfLv7GwpicEXbYEzBfm50qJOk6JQ2Xa2Jebl0DedqHivxUjhHfO8VIJAJXAkorTTYFLtcRYwoqYt7gNS3PF_aeB4CrmrUERK9ZzB6_m6em9h135gOBticnIp6_b3aQaJCmaIKkM0vIJGakj0mO0g_K3nlV7ryKlGfFyqdHtQv3SWI5UuBILTYVQsEH7VzqmwEUW9jA0kbkwP8N8pnU5WwGsgpoZVo1i3np-0doqjCLpb2leB9c-ftAoDoyvhgyvMo7vofSO0eXOmuBQ7WffjPSxLgLtOjfJCIpf__mN-ejftsn0ZWKg_5cUc_A5Km186NsmBbZIfOy7hKN-vqgRnk82yd8gRg_6DjdW6ZL-MR2Kt8_X4AnpwhF57zpbwAAdrIewPGQkas3YeU4qUOiO4LP9P9GTtibL52p8PT2sevBWEoAOq2ozvfjZBJdIrY0DxrpLao_kQuXXSwN_hsCYC94gRzzgNCvtGNefWovC0mYzAGM5HHPNMDhqeDm1aOyviJbhpm8J2TVZVeV4XduPl-0z5RimLiCMaCY732v9P_MbZktzs_MZqAMdY7J", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c2000007c0ce671_0%7C0a220b774c23000067c13b26_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EhTAOsyifNpxqgqaZpriVefuyIGusr-WwMJc_F1VfN4M9wnBwxruDqiDM5LGecKfTht8fqTYwEDMvraa1TaMU_RXfR-0bh_r98w_UVVZdepxPNPiYVy9TXurWbQrrZ9h6RMKsE0D5wc9iDO-dIy_xanJgcZnF4OlhmgdPZL6BTBD7AMHlmzeDPInTDC4iYIIKpEh8I0QlG_qEeV95mSYQyEvLIsu1E7W-2Cpt8dldBqlB0xPXP53i39QnEMSdB_fZuFju27tfLv7GwpicEXbYEzBfm50qJOk6JQ2Xa2Jebl0DedqHivxUjhHfO8VIJAJXAkorTTYFLtcRYwoqYt7gNS3PF_aeB4CrmrUERK9ZzB6_m6em9h135gOBticnIp6_b3aQaJCmaIKkM0vIJGakj0mO0g_K3nlV7ryKlGfFyqdHtQv3SWI5UuBILTYVQsEH7VzqmwEUW9jA0kbkwP8N8pnU5WwGsgpoZVo1i3np-0doqjCLpb2leB9c-ftAoDoyvhgyvMo7vofSO0eXOmuBQ7WffjPSxLgLtOjfJCIpf__mN-ejftsn0ZWKg_5cUc_A5Km186NsmBbZIfOy7hKN-vqgRnk82yd8gRg_6DjdW6ZL-MR2Kt8_X4AnpwhF57zpbwAAdrIewPGQkas3YeU4qUOiO4LP9P9GTtibL52p8PT2sevBWEoAOq2ozvfjZBJdIrY0DxrpLao_kQuXXSwN_hsCYC94gRzzgNCvtGNefWovC0mYzAGM5HHPNMDhqeDm1aOyviJbhpm8J2TVZVeV4XduPl-0z5RimLiCMaCY732v9P_MbZktzs_MZqAMdY7J", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-11T21:15:00.000Z", "utc_arrival": "2023-05-11T19:15:00.000Z", "local_departure": "2023-05-11T17:45:00.000Z", "utc_departure": "2023-05-11T15:45:00.000Z"}, {"id": "0b770a224c320000850ebc30_0|0a220b774c35000063a8527d_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 825.572033, "distance": 1975.87, "duration": {"departure": 12600, "return": 11700, "total": 24300}, "price": 255781.0305, "conversion": {"EUR": 669.572423, "HUF": 255781.0305}, "fare": {"adults": 127890.52, "children": 127890.52, "infants": 127890.52}, "bags_price": {"1": 105.84, "2": 211.68}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 439, "hold_height": 149, "hold_length": 171, "hold_weight": 20, "hold_width": 119, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 2}, "airlines": ["W6"], "route": [{"id": "0b770a224c320000850ebc30_0", "combination_id": "0b770a224c320000850ebc30", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "GHREG", "fare_category": "M", "fare_classes": "G", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-29T19:45:00.000Z", "utc_arrival": "2023-05-29T17:45:00.000Z", "local_departure": "2023-05-29T16:15:00.000Z", "utc_departure": "2023-05-29T14:15:00.000Z"}, {"id": "0a220b774c35000063a8527d_0", "combination_id": "0a220b774c35000063a8527d", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "HIREG", "fare_category": "M", "fare_classes": "H", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-02T01:15:00.000Z", "utc_arrival": "2023-06-01T23:15:00.000Z", "local_departure": "2023-06-01T22:00:00.000Z", "utc_departure": "2023-06-01T20:00:00.000Z"}], "booking_token": "E-7KZyhci2-uS71z44LpJt8p8rGnP3zt_iZy6cC3U1hZ78yTjuj_E0KPr2jnaeYpLXwxSFy7H98tzvzpIusRS0lpB9LtzsRFvHOIDIcsq8Z2m3t9IVKyPVZ1vnYzJpsfnTzcipjwA8lNJwAuYGEKJcARHu1Rd31loToAodi4wiMcpuZxpwFoUecuCS3WCm_FvUAI64nEHUGjOJi8h2Gt9F3Ak0RjLmv2UnBA-czN5ksZP6agytcqzdF3ZQglERJwPt-BFjAP8EEK5C5Igl_zGLzMlu2moRsp8Cnq_-fsphJY1AXY5A2uvZ0dkC9hl14qqlYplz5ZMWY0WBlWtvuofOFeIZCiKVqEOKqJOvlw5qr4Ghs_ToBczWi5X4oVHg3x6hSwdG1Q970eefOvhkjbxKs9OlgP3sTOM5YqJzw0ucgvYpz_2rlla_EHXvYGbVsdposRGWvQf9b9EKF96WNsORBELK1yPBBnc2Lw8MP6ROMxGvZ9GLjdPBlHoh32YJ3iTVADAI4cj8dE0q1NL2MXFbPVho15PvY4zm07ptASu3wKdnaAOql7Ulv7S6M41MgGIwhOHdKMGsbI5zCgfAADVr_ZWiwz1G2PVBmyDBKZmdtF34UoHk5iLA3VG7JLuY2h41hilW9yzTOg24Mk3jV65BAbWo62N-rfN7B93GHkcqRJccpvP2rhenoPDDz-Q1dAjqz0Y3tLcHhwXyh6A9v-VuKzEf2_5lIrqUnpslL9KOC0-iblwthvM6fDSwjJRypAJ-ntHCNN1gcwstxR6sABGqfpxYO3uaJpDmtZMIvgW5k8=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c320000850ebc30_0%7C0a220b774c35000063a8527d_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=E-7KZyhci2-uS71z44LpJt8p8rGnP3zt_iZy6cC3U1hZ78yTjuj_E0KPr2jnaeYpLXwxSFy7H98tzvzpIusRS0lpB9LtzsRFvHOIDIcsq8Z2m3t9IVKyPVZ1vnYzJpsfnTzcipjwA8lNJwAuYGEKJcARHu1Rd31loToAodi4wiMcpuZxpwFoUecuCS3WCm_FvUAI64nEHUGjOJi8h2Gt9F3Ak0RjLmv2UnBA-czN5ksZP6agytcqzdF3ZQglERJwPt-BFjAP8EEK5C5Igl_zGLzMlu2moRsp8Cnq_-fsphJY1AXY5A2uvZ0dkC9hl14qqlYplz5ZMWY0WBlWtvuofOFeIZCiKVqEOKqJOvlw5qr4Ghs_ToBczWi5X4oVHg3x6hSwdG1Q970eefOvhkjbxKs9OlgP3sTOM5YqJzw0ucgvYpz_2rlla_EHXvYGbVsdposRGWvQf9b9EKF96WNsORBELK1yPBBnc2Lw8MP6ROMxGvZ9GLjdPBlHoh32YJ3iTVADAI4cj8dE0q1NL2MXFbPVho15PvY4zm07ptASu3wKdnaAOql7Ulv7S6M41MgGIwhOHdKMGsbI5zCgfAADVr_ZWiwz1G2PVBmyDBKZmdtF34UoHk5iLA3VG7JLuY2h41hilW9yzTOg24Mk3jV65BAbWo62N-rfN7B93GHkcqRJccpvP2rhenoPDDz-Q1dAjqz0Y3tLcHhwXyh6A9v-VuKzEf2_5lIrqUnpslL9KOC0-iblwthvM6fDSwjJRypAJ-ntHCNN1gcwstxR6sABGqfpxYO3uaJpDmtZMIvgW5k8=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-29T19:45:00.000Z", "utc_arrival": "2023-05-29T17:45:00.000Z", "local_departure": "2023-05-29T16:15:00.000Z", "utc_departure": "2023-05-29T14:15:00.000Z"}, {"id": "0b770a224bf20000bc176983_0|0a220b774bf600003991cd2d_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 826.260847, "distance": 1975.87, "duration": {"departure": 12600, "return": 11700, "total": 24300}, "price": 256044.162, "conversion": {"EUR": 670.261237, "HUF": 256044.162}, "fare": {"adults": 128022.08, "children": 131186.41, "infants": 131186.41}, "bags_price": {"1": 97.818, "2": 195.65}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 439, "hold_height": 149, "hold_length": 171, "hold_weight": 20, "hold_width": 119, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 3}, "airlines": ["W6"], "route": [{"id": "0b770a224bf20000bc176983_0", "combination_id": "0b770a224bf20000bc176983", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-03-26T17:05:00.000Z", "utc_arrival": "2023-03-26T15:05:00.000Z", "local_departure": "2023-03-26T13:35:00.000Z", "utc_departure": "2023-03-26T11:35:00.000Z"}, {"id": "0a220b774bf600003991cd2d_0", "combination_id": "0a220b774bf600003991cd2d", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "GHREG", "fare_category": "M", "fare_classes": "G", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-03-31T01:15:00.000Z", "utc_arrival": "2023-03-30T23:15:00.000Z", "local_departure": "2023-03-30T22:00:00.000Z", "utc_departure": "2023-03-30T20:00:00.000Z"}], "booking_token": "EQdMhLyi_NeHAgsOEMlfKHej0JWKDZDvbXyxdBOu97mbuN_E_vk8f1VyAtHl6wMHhC3BGcdxvJjiodyOaIruIOQFupir-qKKgBgeFoElNJeYa2aVuPQjvslzlX1QXqcw_76SSCcYvP4ByTsgXEDQFoiL8yDefDBrqiGvReA-7qlwr7x1qAKsuqnTFK_rIZVapz4kAG8XccjFMhsr7-1ksERO4MHIZ5wMz7PaD38dvgesula3Ux_cuNz5hf7oCwlohriagyYJbCAbiY_M159eZyliq81OkVq9D1zvbM9UsteFLlqHo8Z9hD1augGhi8C9hXzgbOHDYPaaRc7jvt9JHRvTXHBQi2ogVB8yt7xL9piQ7sgFKycG2ixff6eK-LVkKTkMrQ642HXGLkalAHpqdRi4EKW4Tq_c0uZABC_Ff3vP7em2sY_vd_Q2Pn1ozfMNL6c1w5W8ggMeffzFuEZ0ORZA8CzA70pRx3V0O8CwGJWrviTt8oDv04C8a5zPOedk64LqR5TBk9qLu2CXy7Y9CqTb-e8-dIvraM2gYm6R8XmHWSlFYHah1aA4ng5NuyBF6VYYnSqYUREx_W5QS796CqHC8xSQRZAkSSksZ5SKM0A8179x1PseW2r_cEnP-jl3kfjcJrz4esJp6Lvs0f3BSb5tIu3l78wD6F59apgiWu6c0tAx60pYRofVNQ6E8TV3g5HfEC3cLoiYhAozbUvur-OgYns2M6qrySM8e3x6bc1b8fOr9TsJiYDkbU3aXYV8H-OWW6hOXyVTKnyzepYjv43y777SscS3mNjqJoUX7IMc=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224bf20000bc176983_0%7C0a220b774bf600003991cd2d_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EQdMhLyi_NeHAgsOEMlfKHej0JWKDZDvbXyxdBOu97mbuN_E_vk8f1VyAtHl6wMHhC3BGcdxvJjiodyOaIruIOQFupir-qKKgBgeFoElNJeYa2aVuPQjvslzlX1QXqcw_76SSCcYvP4ByTsgXEDQFoiL8yDefDBrqiGvReA-7qlwr7x1qAKsuqnTFK_rIZVapz4kAG8XccjFMhsr7-1ksERO4MHIZ5wMz7PaD38dvgesula3Ux_cuNz5hf7oCwlohriagyYJbCAbiY_M159eZyliq81OkVq9D1zvbM9UsteFLlqHo8Z9hD1augGhi8C9hXzgbOHDYPaaRc7jvt9JHRvTXHBQi2ogVB8yt7xL9piQ7sgFKycG2ixff6eK-LVkKTkMrQ642HXGLkalAHpqdRi4EKW4Tq_c0uZABC_Ff3vP7em2sY_vd_Q2Pn1ozfMNL6c1w5W8ggMeffzFuEZ0ORZA8CzA70pRx3V0O8CwGJWrviTt8oDv04C8a5zPOedk64LqR5TBk9qLu2CXy7Y9CqTb-e8-dIvraM2gYm6R8XmHWSlFYHah1aA4ng5NuyBF6VYYnSqYUREx_W5QS796CqHC8xSQRZAkSSksZ5SKM0A8179x1PseW2r_cEnP-jl3kfjcJrz4esJp6Lvs0f3BSb5tIu3l78wD6F59apgiWu6c0tAx60pYRofVNQ6E8TV3g5HfEC3cLoiYhAozbUvur-OgYns2M6qrySM8e3x6bc1b8fOr9TsJiYDkbU3aXYV8H-OWW6hOXyVTKnyzepYjv43y777SscS3mNjqJoUX7IMc=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-03-26T17:05:00.000Z", "utc_arrival": "2023-03-26T15:05:00.000Z", "local_departure": "2023-03-26T13:35:00.000Z", "utc_departure": "2023-03-26T11:35:00.000Z"}, {"id": "0b770a224bfa0000e3b3cbb8_0|0a220b774bfe000002ec78b7_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 823.039992, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 256341.7966, "conversion": {"EUR": 671.040372, "HUF": 256341.7966}, "fare": {"adults": 128170.9, "children": 128170.9, "infants": 128170.9}, "bags_price": {"1": 109.018, "2": 190.946}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 5}, "airlines": ["FR"], "route": [{"id": "0b770a224bfa0000e3b3cbb8_0", "combination_id": "0b770a224bfa0000e3b3cbb8", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-03T14:00:00.000Z", "utc_arrival": "2023-04-03T12:00:00.000Z", "local_departure": "2023-04-03T10:40:00.000Z", "utc_departure": "2023-04-03T08:40:00.000Z"}, {"id": "0a220b774bfe000002ec78b7_0", "combination_id": "0a220b774bfe000002ec78b7", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-07T18:00:00.000Z", "utc_arrival": "2023-04-07T16:00:00.000Z", "local_departure": "2023-04-07T14:50:00.000Z", "utc_departure": "2023-04-07T12:50:00.000Z"}], "booking_token": "EsULbZu0DRRtKhdzuGmLqYlk2O2mdCK4skNGYualEHRa5RdSL3DWXzCfJ2GSxwKYiEtYEWvw4Zf1U2S8mtVWwapyQqgvJFm077NZVQSW8gJoRQtqpggUwY_Ef9L7MaIekNsBpEkcNv9n95GlpaYUcPftBMd9_HcPm_UDqU3DYLll294UIdhSSCE0VsFBpErftRxWcyAerrdRp6TtqmQ1G3fkxnvYuPwsez7nEogskMzKob6POjNvW-jPCc0syM-c2x-_jMAjlBIC_aMwswmj3VSiCk371H_ZfNFyIWEkNDAwd6iHhw24_GhoCv65QyOTj7wUGNU2h3ErxxS_rl20W6BKcQ3A9v2pVILT_OquFkDpHpvlx458mC7lsPN2KFRc37wHb7wBBOTpHCZxURmqnJqkGcsz3z8ODXM6bN-CznBAbC1JxRHYBeGmF5N1gFtbh40K_FlRP2f64iKk5Jefhw-66tpbomaThHRNWgB47d8Wd3B4SdtVoOIvUyp932Pf0K4gAQSb7JMXqBk5P13GuMKm8GQemV8_Tm8bgO8LEq-FCH0on_xO6_WSFlIJ81QIK-qC49Q-wup94JnYaQl2VhmLzaUcc0k80P4cMJy8xlOigMAfH7ToIBmv13k70q4U03JoYI4mV-9wSSk5ZeFl36cqjhky7ivJX_T6PidbMXLohmUW8K2cr59UCCpoG03pQTng0ofhievI5kUaDfBijJDty3Tm9Qut8n_HjvNy1IPdjd626dch26Nub-IvZM05zUeybTwFXonWpby_zXJvL0Q==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224bfa0000e3b3cbb8_0%7C0a220b774bfe000002ec78b7_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EsULbZu0DRRtKhdzuGmLqYlk2O2mdCK4skNGYualEHRa5RdSL3DWXzCfJ2GSxwKYiEtYEWvw4Zf1U2S8mtVWwapyQqgvJFm077NZVQSW8gJoRQtqpggUwY_Ef9L7MaIekNsBpEkcNv9n95GlpaYUcPftBMd9_HcPm_UDqU3DYLll294UIdhSSCE0VsFBpErftRxWcyAerrdRp6TtqmQ1G3fkxnvYuPwsez7nEogskMzKob6POjNvW-jPCc0syM-c2x-_jMAjlBIC_aMwswmj3VSiCk371H_ZfNFyIWEkNDAwd6iHhw24_GhoCv65QyOTj7wUGNU2h3ErxxS_rl20W6BKcQ3A9v2pVILT_OquFkDpHpvlx458mC7lsPN2KFRc37wHb7wBBOTpHCZxURmqnJqkGcsz3z8ODXM6bN-CznBAbC1JxRHYBeGmF5N1gFtbh40K_FlRP2f64iKk5Jefhw-66tpbomaThHRNWgB47d8Wd3B4SdtVoOIvUyp932Pf0K4gAQSb7JMXqBk5P13GuMKm8GQemV8_Tm8bgO8LEq-FCH0on_xO6_WSFlIJ81QIK-qC49Q-wup94JnYaQl2VhmLzaUcc0k80P4cMJy8xlOigMAfH7ToIBmv13k70q4U03JoYI4mV-9wSSk5ZeFl36cqjhky7ivJX_T6PidbMXLohmUW8K2cr59UCCpoG03pQTng0ofhievI5kUaDfBijJDty3Tm9Qut8n_HjvNy1IPdjd626dch26Nub-IvZM05zUeybTwFXonWpby_zXJvL0Q==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-04-03T14:00:00.000Z", "utc_arrival": "2023-04-03T12:00:00.000Z", "local_departure": "2023-04-03T10:40:00.000Z", "utc_departure": "2023-04-03T08:40:00.000Z"}, {"id": "0b770a224c2f0000c413678f_0|0a220b774c3200001b9f20d5_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 827.13026, "distance": 1975.87, "duration": {"departure": 12600, "return": 11700, "total": 24300}, "price": 256376.2834, "conversion": {"EUR": 671.13065, "HUF": 256376.2834}, "fare": {"adults": 128188.14, "children": 131143.83, "infants": 131143.83}, "bags_price": {"1": 93.436, "2": 186.872}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 439, "hold_height": 149, "hold_length": 171, "hold_weight": 20, "hold_width": 119, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 2}, "airlines": ["W6"], "route": [{"id": "0b770a224c2f0000c413678f_0", "combination_id": "0b770a224c2f0000c413678f", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-26T19:45:00.000Z", "utc_arrival": "2023-05-26T17:45:00.000Z", "local_departure": "2023-05-26T16:15:00.000Z", "utc_departure": "2023-05-26T14:15:00.000Z"}, {"id": "0a220b774c3200001b9f20d5_0", "combination_id": "0a220b774c3200001b9f20d5", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "GREG", "fare_category": "M", "fare_classes": "G", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-29T23:45:00.000Z", "utc_arrival": "2023-05-29T21:45:00.000Z", "local_departure": "2023-05-29T20:30:00.000Z", "utc_departure": "2023-05-29T18:30:00.000Z"}], "booking_token": "E7oU1-qFzPjMVkOhgIARCrxk4KzO1isxTbtJBRonBRBRaOg6dxQPuvFjxMALWVXtsMHz0v1kpySGxT1zAz__u3vKL295UlKHeIFFQpFHPboy3-1ER0mvovkFiXIKjphA3mL_rh863bm4_nPqRG2uteD83M6LGXNr0ZO9795KGvkyQdMlqPJh3KNFG8PjhlyvkrbgwLgJrGNptIEvifTxt7SmSJY9jzbQLOETYqGUuzHP9gwF0-H6k6XdCN22cbT86kZ1p3f7eWX2wwhmHk_hJ2z_oQ1OkWXMc-0HOHBzPlG-AdLss1h1bbL6-EguYTjlLL9XGF0W-y9gcSZv-okjomTsvCOsgETu0_W_bc8PJDWmGYdlhhUUwTMe-jsBoKmypXxaMyBSmm_jGn1d0XO2XXpTPzveCHF-6rtbZo3pbG9_S1-MxHsfaRObiRBEak_OZgJnxFrngHoIodgZ0njiih_bfoufnvrdYkN91MT6iO8WjKR2orCOsp5CsovLk_rcdxbEwMdpbDowJEDPUnwNgezrViC_dC7Oh6FBgvKlaQ7W6UqJZ48RQnAUhEzA5Qs5HTC5sWcXTFv9UEaoqW6Wm78vYxQUJ8Pc-bfncoTrlEis_OlLBk-2ejLA_0aCJC71Ta5YiNKGxdimvjYJua_Ox9z6fqWZ9Z7CQIec_4dBdzh60aIFmC3O1MIq4JBl5usb9BY1tZ7dcBKZYI51hNCZNfJDFxy8Duy4OxiX4vrrcDTKJ3NDmw8TL_0XepdBjcgejxhdFIQxwJPJJGURLJ8WJgW9YyGBbA5IinRrDzsgnxSg=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c2f0000c413678f_0%7C0a220b774c3200001b9f20d5_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=E7oU1-qFzPjMVkOhgIARCrxk4KzO1isxTbtJBRonBRBRaOg6dxQPuvFjxMALWVXtsMHz0v1kpySGxT1zAz__u3vKL295UlKHeIFFQpFHPboy3-1ER0mvovkFiXIKjphA3mL_rh863bm4_nPqRG2uteD83M6LGXNr0ZO9795KGvkyQdMlqPJh3KNFG8PjhlyvkrbgwLgJrGNptIEvifTxt7SmSJY9jzbQLOETYqGUuzHP9gwF0-H6k6XdCN22cbT86kZ1p3f7eWX2wwhmHk_hJ2z_oQ1OkWXMc-0HOHBzPlG-AdLss1h1bbL6-EguYTjlLL9XGF0W-y9gcSZv-okjomTsvCOsgETu0_W_bc8PJDWmGYdlhhUUwTMe-jsBoKmypXxaMyBSmm_jGn1d0XO2XXpTPzveCHF-6rtbZo3pbG9_S1-MxHsfaRObiRBEak_OZgJnxFrngHoIodgZ0njiih_bfoufnvrdYkN91MT6iO8WjKR2orCOsp5CsovLk_rcdxbEwMdpbDowJEDPUnwNgezrViC_dC7Oh6FBgvKlaQ7W6UqJZ48RQnAUhEzA5Qs5HTC5sWcXTFv9UEaoqW6Wm78vYxQUJ8Pc-bfncoTrlEis_OlLBk-2ejLA_0aCJC71Ta5YiNKGxdimvjYJua_Ox9z6fqWZ9Z7CQIec_4dBdzh60aIFmC3O1MIq4JBl5usb9BY1tZ7dcBKZYI51hNCZNfJDFxy8Duy4OxiX4vrrcDTKJ3NDmw8TL_0XepdBjcgejxhdFIQxwJPJJGURLJ8WJgW9YyGBbA5IinRrDzsgnxSg=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-26T19:45:00.000Z", "utc_arrival": "2023-05-26T17:45:00.000Z", "local_departure": "2023-05-26T16:15:00.000Z", "utc_departure": "2023-05-26T14:15:00.000Z"}, {"id": "0b770a224c0e00005b90efbb_0|0a220b774c1200004e293ac3_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 827.898886, "distance": 1975.87, "duration": {"departure": 12600, "return": 11700, "total": 24300}, "price": 256669.9035, "conversion": {"EUR": 671.899276, "HUF": 256669.9035}, "fare": {"adults": 128334.95, "children": 128334.95, "infants": 128334.95}, "bags_price": {"1": 118.02, "2": 236.04}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 439, "hold_height": 149, "hold_length": 171, "hold_weight": 20, "hold_width": 119, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 4}, "airlines": ["W6"], "route": [{"id": "0b770a224c0e00005b90efbb_0", "combination_id": "0b770a224c0e00005b90efbb", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "JREG", "fare_category": "M", "fare_classes": "J", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-23T17:05:00.000Z", "utc_arrival": "2023-04-23T15:05:00.000Z", "local_departure": "2023-04-23T13:35:00.000Z", "utc_departure": "2023-04-23T11:35:00.000Z"}, {"id": "0a220b774c1200004e293ac3_0", "combination_id": "0a220b774c1200004e293ac3", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "GFREG", "fare_category": "M", "fare_classes": "G", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-28T01:15:00.000Z", "utc_arrival": "2023-04-27T23:15:00.000Z", "local_departure": "2023-04-27T22:00:00.000Z", "utc_departure": "2023-04-27T20:00:00.000Z"}], "booking_token": "EV5ZGU8q9VWYTfOOGf082QoG_GFi64QBh-lRNyuZbMshQtWwlhwWe26RQbWeOrpOn4YgohvyBzMoZ4qxYLlBIIsa7Dd60Md2Gjoh7DuujDW4feA66TUdQGnFF_armoK_gU1BPTyDe79me4mtY5GJ5lEBAA5qYd_71FcOTZTZjvFqstaD5-rW27CiYSCAFWpr9goi9y9z_GF5I8qNWmhJTP6CypBUKc6EF0YQXwWpz5Dw-icl1BfWuWDMiV6a_gN1JJo0-PJDafCDFHeX9NDKuNp-39u0192fRlPZ3ApNvBfZO3jhD9VEsIDRZKDtjzwz-tctWkF1gZ3OwHRbrH-xaUJnHYwgj-S3yzKcf5EhZ2Jsz5EZBR2sD-5OYn8KtPFXgFOmE7NrOb5gn8C_K2WhilYlEZE9QscQfIyypySzs62qmCCehlKbMlIhqXRJoMUHaN_BJ6xsXL7NFGJf8eOE1IsRk4qmUx0pav7vEe3SNbAZzEUv_Ya5Dxl80T_CE1TP_si7UWw6fcnM8BRN7rP2FotOVjBfbY5g11NQlWI6ZyZlEAW91XbYXsqputnvGRbapGSbk9iJD9tMmYc6ktuVCeyXr7gcL3pflvpEYwtVG6Xivnd9csU8WxVo1I_PC_ZL1ahW2qtoxtJHh1bQQ2OEse8uLfcwvfrqRwshINRR03-lWjHr9m0Ib3MyUd5MC4h75xhDSCjuFqNJ4wj5MF1YCt0NFaGQgU6BU9vezmyCmbO9knEHLOZatLD3UtwuYbHmRb3J2DWUteXxAG2yNJj-649mfKc7y6YpGisrjZznTR74=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c0e00005b90efbb_0%7C0a220b774c1200004e293ac3_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EV5ZGU8q9VWYTfOOGf082QoG_GFi64QBh-lRNyuZbMshQtWwlhwWe26RQbWeOrpOn4YgohvyBzMoZ4qxYLlBIIsa7Dd60Md2Gjoh7DuujDW4feA66TUdQGnFF_armoK_gU1BPTyDe79me4mtY5GJ5lEBAA5qYd_71FcOTZTZjvFqstaD5-rW27CiYSCAFWpr9goi9y9z_GF5I8qNWmhJTP6CypBUKc6EF0YQXwWpz5Dw-icl1BfWuWDMiV6a_gN1JJo0-PJDafCDFHeX9NDKuNp-39u0192fRlPZ3ApNvBfZO3jhD9VEsIDRZKDtjzwz-tctWkF1gZ3OwHRbrH-xaUJnHYwgj-S3yzKcf5EhZ2Jsz5EZBR2sD-5OYn8KtPFXgFOmE7NrOb5gn8C_K2WhilYlEZE9QscQfIyypySzs62qmCCehlKbMlIhqXRJoMUHaN_BJ6xsXL7NFGJf8eOE1IsRk4qmUx0pav7vEe3SNbAZzEUv_Ya5Dxl80T_CE1TP_si7UWw6fcnM8BRN7rP2FotOVjBfbY5g11NQlWI6ZyZlEAW91XbYXsqputnvGRbapGSbk9iJD9tMmYc6ktuVCeyXr7gcL3pflvpEYwtVG6Xivnd9csU8WxVo1I_PC_ZL1ahW2qtoxtJHh1bQQ2OEse8uLfcwvfrqRwshINRR03-lWjHr9m0Ib3MyUd5MC4h75xhDSCjuFqNJ4wj5MF1YCt0NFaGQgU6BU9vezmyCmbO9knEHLOZatLD3UtwuYbHmRb3J2DWUteXxAG2yNJj-649mfKc7y6YpGisrjZznTR74=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-04-23T17:05:00.000Z", "utc_arrival": "2023-04-23T15:05:00.000Z", "local_departure": "2023-04-23T13:35:00.000Z", "utc_departure": "2023-04-23T11:35:00.000Z"}, {"id": "0b770a224bf90000ce0a1274_0|0a220b774bfd0000e604e9be_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 829.199841, "distance": 1975.87, "duration": {"departure": 12600, "return": 11700, "total": 24300}, "price": 257166.8768, "conversion": {"EUR": 673.200231, "HUF": 257166.8768}, "fare": {"adults": 128583.44, "children": 131745.78, "infants": 131745.78}, "bags_price": {"1": 110.6, "2": 221.2}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 439, "hold_height": 149, "hold_length": 171, "hold_weight": 20, "hold_width": 119, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 3}, "airlines": ["W6"], "route": [{"id": "0b770a224bf90000ce0a1274_0", "combination_id": "0b770a224bf90000ce0a1274", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "GHREG", "fare_category": "M", "fare_classes": "G", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-02T17:05:00.000Z", "utc_arrival": "2023-04-02T15:05:00.000Z", "local_departure": "2023-04-02T13:35:00.000Z", "utc_departure": "2023-04-02T11:35:00.000Z"}, {"id": "0a220b774bfd0000e604e9be_0", "combination_id": "0a220b774bfd0000e604e9be", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-07T01:15:00.000Z", "utc_arrival": "2023-04-06T23:15:00.000Z", "local_departure": "2023-04-06T22:00:00.000Z", "utc_departure": "2023-04-06T20:00:00.000Z"}], "booking_token": "EFIx9gtYlZLsyRVwxJ8Jk_6xXwg2c6P3n9tVR6RmrswdrlXdlHU9apo3z1tGeCaJLl-BcoHn6oTD8NEAlvtz5yNqiIHjRubVkMxOLefIpeTqC9snjA_SkyfHsUnymFl4EB_BBEU1U8MkFm7jun39tyNiROk3csU8A76DnedNSF3vcbjlfXkVWsvYvgl2OXNS-VjlB6cQUVTmdEpoqXSmOGpwPIe78BlK7M6vdDm4WeFdJn97K_sleMlsKRbc2Q38hBnIV09x2_jt9CE1dM_cS-4bg1v1xIS-aOO-f1ODAXL52S2qHyYunMPP3yWrba57FhZ-EWV6fnLVG8tpuQnwFf0aNmkvZi62TokLPx6ihcd-NJE_KFJELhJutZSlYBR6yHuACecliXszZQE0FRSudnoUQc16J5Y5ngtQHdGKe8A8J6ffXIbhES-Rt7ULPN4Hrs6Ew5KNZiMLbIEXsSApeJ9OXv1RalJr-NVk-acx-WORf9y5FALF6xJhfa3qVZpoc_vMSIguMBfP-w6qhcRd0H3noib6PHq81JYNh5e2xTLB8za2WVSN8FX_h6aZE6l-bj5vvXjTt8Z19zifUpgw9FTMea3R93WREm7lGFm0VzaIf1BXBJXn_ntVU7bCRAj9UHiYVO7WrOlmQEM5SSSmzplY6biS-I-XomrdYInKu7UfgqUkpPLFWsIiZJzs9XHD-DFj34tUbtPvG-Hl8H79KKaaXCfBs35JB08sHP-sHhbYI2F7_rq4NhI_vRGVfqKgfQNcCaUmqrTMWstbMJkBCBg==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224bf90000ce0a1274_0%7C0a220b774bfd0000e604e9be_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EFIx9gtYlZLsyRVwxJ8Jk_6xXwg2c6P3n9tVR6RmrswdrlXdlHU9apo3z1tGeCaJLl-BcoHn6oTD8NEAlvtz5yNqiIHjRubVkMxOLefIpeTqC9snjA_SkyfHsUnymFl4EB_BBEU1U8MkFm7jun39tyNiROk3csU8A76DnedNSF3vcbjlfXkVWsvYvgl2OXNS-VjlB6cQUVTmdEpoqXSmOGpwPIe78BlK7M6vdDm4WeFdJn97K_sleMlsKRbc2Q38hBnIV09x2_jt9CE1dM_cS-4bg1v1xIS-aOO-f1ODAXL52S2qHyYunMPP3yWrba57FhZ-EWV6fnLVG8tpuQnwFf0aNmkvZi62TokLPx6ihcd-NJE_KFJELhJutZSlYBR6yHuACecliXszZQE0FRSudnoUQc16J5Y5ngtQHdGKe8A8J6ffXIbhES-Rt7ULPN4Hrs6Ew5KNZiMLbIEXsSApeJ9OXv1RalJr-NVk-acx-WORf9y5FALF6xJhfa3qVZpoc_vMSIguMBfP-w6qhcRd0H3noib6PHq81JYNh5e2xTLB8za2WVSN8FX_h6aZE6l-bj5vvXjTt8Z19zifUpgw9FTMea3R93WREm7lGFm0VzaIf1BXBJXn_ntVU7bCRAj9UHiYVO7WrOlmQEM5SSSmzplY6biS-I-XomrdYInKu7UfgqUkpPLFWsIiZJzs9XHD-DFj34tUbtPvG-Hl8H79KKaaXCfBs35JB08sHP-sHhbYI2F7_rq4NhI_vRGVfqKgfQNcCaUmqrTMWstbMJkBCBg==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-04-02T17:05:00.000Z", "utc_arrival": "2023-04-02T15:05:00.000Z", "local_departure": "2023-04-02T13:35:00.000Z", "utc_departure": "2023-04-02T11:35:00.000Z"}, {"id": "0b770a224c470000e38f46b1_0|0a220b774c4a000044c8cf5d_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 826.197021, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 257547.8023, "conversion": {"EUR": 674.197401, "HUF": 257547.8023}, "fare": {"adults": 128773.9, "children": 128773.9, "infants": 128773.9}, "bags_price": {"1": 76.706, "2": 163.212}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 158, "hold_height": 52, "hold_length": 78, "hold_weight": 20, "hold_width": 28, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 3, "personal_item_width": 15}, "availability": {"seats": 4}, "airlines": ["FR", "IB"], "route": [{"id": "0b770a224c470000e38f46b1_0", "combination_id": "0b770a224c470000e38f46b1", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-19T14:00:00.000Z", "utc_arrival": "2023-06-19T12:00:00.000Z", "local_departure": "2023-06-19T10:40:00.000Z", "utc_departure": "2023-06-19T08:40:00.000Z"}, {"id": "0a220b774c4a000044c8cf5d_0", "combination_id": "0a220b774c4a000044c8cf5d", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "IB", "flight_no": 3278, "operating_carrier": "IB", "operating_flight_no": "3278", "fare_basis": "VZNNAOB4", "fare_category": "M", "fare_classes": "V", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-22T14:55:00.000Z", "utc_arrival": "2023-06-22T12:55:00.000Z", "local_departure": "2023-06-22T11:45:00.000Z", "utc_departure": "2023-06-22T09:45:00.000Z"}], "booking_token": "EndC_yjs2jp65JCI6J3p3T9_Hy7-qddVWuOGBm_kNk4mlpbo8D9ln7LZCIJJBfEBOrcoktWYJbQYJAM_evHufMDbzlEsfNBsSwrlAy3XMXydw3aNCIjxXXsH431x_ymPn7TLu5IBixtusTt6zw-TYLMUU79bRvtGCpqDD2qxlknAM9sGsdkTwINLOrMAcc1su_7X7tqWDfqGie9QMP4o8Jy9J2pWsGQdg3b9gtCBCdrc9GDpH8PlPsoYEXlZ7exKnlpsoSAOO9GnFJqW33MBCfAXJPf6xBwxhb4-uZdJlgBb2tPxZ7PibJhGsSOBRLU1rdVcVRsBhZkGnAv5998eohjUsyNm-LkjLzX-mcUXDl0QcwVlYi7v1ItiiHBacNRFQFcJUfdtuKY-w-JHwBnnoosHyvyVUE9v6tFU0ES8EnSY9W3yxlP_RFgF-5E58xYtnFOMVKT9i14CzjDHHozds_rKkMG7rogFE2t43IejjIgVHFB3msUaclFQUFIr7XCtzcGBGKhUoTJJIwForfXuFFxBme5UG2vHGVKEqj7WNjY6gH_wov-2uOU2vkUU6yrPxQ7eEiggSLeBHvMMtvd69bG8Xk-XBnFcwv2ydyb0y4bJG_1ZQhQ6fOTguireKplfwlqgB_5spVp0Ax0XIcyXbD6OHG5UQOqkr8E8nOh_QTy3RiK7PHW-VN_6JVkwrrObCuovWhFaAfLxwRQ866VILL29wzW8YHxjL6utWnhvvkUm3ckt-U9UoXN7eHsPDlsTaAOQaSoYvUD-RkeSwDah0LT39hsIkm_qtdgntjtRmAOg=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c470000e38f46b1_0%7C0a220b774c4a000044c8cf5d_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EndC_yjs2jp65JCI6J3p3T9_Hy7-qddVWuOGBm_kNk4mlpbo8D9ln7LZCIJJBfEBOrcoktWYJbQYJAM_evHufMDbzlEsfNBsSwrlAy3XMXydw3aNCIjxXXsH431x_ymPn7TLu5IBixtusTt6zw-TYLMUU79bRvtGCpqDD2qxlknAM9sGsdkTwINLOrMAcc1su_7X7tqWDfqGie9QMP4o8Jy9J2pWsGQdg3b9gtCBCdrc9GDpH8PlPsoYEXlZ7exKnlpsoSAOO9GnFJqW33MBCfAXJPf6xBwxhb4-uZdJlgBb2tPxZ7PibJhGsSOBRLU1rdVcVRsBhZkGnAv5998eohjUsyNm-LkjLzX-mcUXDl0QcwVlYi7v1ItiiHBacNRFQFcJUfdtuKY-w-JHwBnnoosHyvyVUE9v6tFU0ES8EnSY9W3yxlP_RFgF-5E58xYtnFOMVKT9i14CzjDHHozds_rKkMG7rogFE2t43IejjIgVHFB3msUaclFQUFIr7XCtzcGBGKhUoTJJIwForfXuFFxBme5UG2vHGVKEqj7WNjY6gH_wov-2uOU2vkUU6yrPxQ7eEiggSLeBHvMMtvd69bG8Xk-XBnFcwv2ydyb0y4bJG_1ZQhQ6fOTguireKplfwlqgB_5spVp0Ax0XIcyXbD6OHG5UQOqkr8E8nOh_QTy3RiK7PHW-VN_6JVkwrrObCuovWhFaAfLxwRQ866VILL29wzW8YHxjL6utWnhvvkUm3ckt-U9UoXN7eHsPDlsTaAOQaSoYvUD-RkeSwDah0LT39hsIkm_qtdgntjtRmAOg=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-19T14:00:00.000Z", "utc_arrival": "2023-06-19T12:00:00.000Z", "local_departure": "2023-06-19T10:40:00.000Z", "utc_departure": "2023-06-19T08:40:00.000Z"}, {"id": "0b770a224c320000850ebc30_0|0a220b774c36000010c6991f_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 829.581681, "distance": 1975.87, "duration": {"departure": 12600, "return": 11400, "total": 24000}, "price": 257822.083, "conversion": {"EUR": 674.915401, "HUF": 257822.083}, "fare": {"adults": 128911.04, "children": 128911.04, "infants": 128911.04}, "bags_price": {"1": 86.926, "2": 173.852}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 2}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224c320000850ebc30_0", "combination_id": "0b770a224c320000850ebc30", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "GHREG", "fare_category": "M", "fare_classes": "G", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-29T19:45:00.000Z", "utc_arrival": "2023-05-29T17:45:00.000Z", "local_departure": "2023-05-29T16:15:00.000Z", "utc_departure": "2023-05-29T14:15:00.000Z"}, {"id": "0a220b774c36000010c6991f_0", "combination_id": "0a220b774c36000010c6991f", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-02T18:00:00.000Z", "utc_arrival": "2023-06-02T16:00:00.000Z", "local_departure": "2023-06-02T14:50:00.000Z", "utc_departure": "2023-06-02T12:50:00.000Z"}], "booking_token": "EMwQ88Hwdymms-PG22Eh96valyp75MfRnRJcBAXs5XUUckzhvv36ZRvzr4rCg59A8U22jg1Gg5sWPz9oAq54CsyjS9sNjLs8U3iZRL7E_Yobk_-QCkQklC0pVXGgyrAZR45yuKR9-OqUxjewz4c5ER-BEWtkC643H0lblmu8MoRfnVXTMX2LlvG9JD9YMZRQ-Afhih-bYdVJeOOfYrAlZaCSsz4nebghGiQjTYDlW6tay35IorbiptOyrLJuPej6jWsuK023uPVvyTxaQBrcakb7biOu6a8lj9DJktWPMSGKxrRftwAvZv-U1NO9SJPq5JX8G7N6oog-GJ-zWNpjizmslMddzByi-4S5xCw3OQJFbtBgj1xImbSwg4XugTpBVpkk4N0TSVJ-f5hyFJxGrG9c6Sc8xVRuWIbx6KogmkspYc_7McSNcwtmGxaLzaM_Ljg0XFyhy0DAVpDaGzRqX3XvnukSgMQdsGre8h5Xf_NQbW1RTFTfPtFDUW0PaWZ2pxfFHNclSd4yWcXAkBS3XWgGGtklZST3VHqCCCRizMQXkaNjTjSUriXW-TfQtQ7GQJ_Ol9KNtVXacKpyTIpUyKvEVbtbm5yAoq2jpIl8uo69GSRB3GGET3SECWvyky03xebML-d8AOagElVnds2BjdGO7e4JNPDCX8pv9cDHwjQYW8J96sPIXHQLegxrFgHKIgv6w7qrvGe53txQ6FderLpI3fY129KI07i4k-VkUkwRLUViMxT7syskgz90mcxov9ZEHHgSEaygPCvXTDGyeXw==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c320000850ebc30_0%7C0a220b774c36000010c6991f_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EMwQ88Hwdymms-PG22Eh96valyp75MfRnRJcBAXs5XUUckzhvv36ZRvzr4rCg59A8U22jg1Gg5sWPz9oAq54CsyjS9sNjLs8U3iZRL7E_Yobk_-QCkQklC0pVXGgyrAZR45yuKR9-OqUxjewz4c5ER-BEWtkC643H0lblmu8MoRfnVXTMX2LlvG9JD9YMZRQ-Afhih-bYdVJeOOfYrAlZaCSsz4nebghGiQjTYDlW6tay35IorbiptOyrLJuPej6jWsuK023uPVvyTxaQBrcakb7biOu6a8lj9DJktWPMSGKxrRftwAvZv-U1NO9SJPq5JX8G7N6oog-GJ-zWNpjizmslMddzByi-4S5xCw3OQJFbtBgj1xImbSwg4XugTpBVpkk4N0TSVJ-f5hyFJxGrG9c6Sc8xVRuWIbx6KogmkspYc_7McSNcwtmGxaLzaM_Ljg0XFyhy0DAVpDaGzRqX3XvnukSgMQdsGre8h5Xf_NQbW1RTFTfPtFDUW0PaWZ2pxfFHNclSd4yWcXAkBS3XWgGGtklZST3VHqCCCRizMQXkaNjTjSUriXW-TfQtQ7GQJ_Ol9KNtVXacKpyTIpUyKvEVbtbm5yAoq2jpIl8uo69GSRB3GGET3SECWvyky03xebML-d8AOagElVnds2BjdGO7e4JNPDCX8pv9cDHwjQYW8J96sPIXHQLegxrFgHKIgv6w7qrvGe53txQ6FderLpI3fY129KI07i4k-VkUkwRLUViMxT7syskgz90mcxov9ZEHHgSEaygPCvXTDGyeXw==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-29T19:45:00.000Z", "utc_arrival": "2023-05-29T17:45:00.000Z", "local_departure": "2023-05-29T16:15:00.000Z", "utc_departure": "2023-05-29T14:15:00.000Z"}, {"id": "0b770a224c1d00001b98d770_0|0a220b774c200000e29d7a94_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 830.003828, "distance": 1975.87, "duration": {"departure": 12000, "return": 11700, "total": 23700}, "price": 258492.6866, "conversion": {"EUR": 676.670878, "HUF": 258492.6866}, "fare": {"adults": 129246.34, "children": 129246.34, "infants": 129246.34}, "bags_price": {"1": 76.72, "2": 153.44}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 5}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224c1d00001b98d770_0", "combination_id": "0b770a224c1d00001b98d770", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-08T14:00:00.000Z", "utc_arrival": "2023-05-08T12:00:00.000Z", "local_departure": "2023-05-08T10:40:00.000Z", "utc_departure": "2023-05-08T08:40:00.000Z"}, {"id": "0a220b774c200000e29d7a94_0", "combination_id": "0a220b774c200000e29d7a94", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "HREG", "fare_category": "M", "fare_classes": "H", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-12T01:15:00.000Z", "utc_arrival": "2023-05-11T23:15:00.000Z", "local_departure": "2023-05-11T22:00:00.000Z", "utc_departure": "2023-05-11T20:00:00.000Z"}], "booking_token": "EOAtQo_Jsnz9XH5kW63MBNxjx7TVmqnx4WYIDdz3dShUorcSPPuF_GeCF50qJ6XzqaI8vaf1x_YZzEs30BlQvTKggdFkZK5Stx-FmqNlOeX1D_6nu_SGsHkPot7HkcVNqxVyVzkSt-h1e6XacFEz1ieXPgqVpBvaxdk6d9EsCJCzwzgVDWbYN983jlIRlEuzmb2xZLIEDSf9igWezE-UB-H7BlDgg1PgrV11tu5zWFpjqiRVHS689ksWuoD8T_ONcfOqnMlPFS1znyNvTbVrlJqwnkoNKI7nIbF-0_qFOKakOgaIjmyHTpprwU1o0QC4Pf1sR9HhsJZV-f2UQOnPDf0LPMKdtCocvA-OloUrs7cjodPgWFc1gPKRp05VGyDQI-dBYYMaj4D6FxkstJWrMe2hsp92wT14OlnMYs7INi6vb7_ZsanNiRsjT4PRq6w04rE80oQKYb7RHVL2TPDPrNMVjHtkme1vmB7CZNHOU-AJ7IH5YYjhHiJMhPDnzBKvri0FCmKWetn9WtfgP0vOEG7usklbfbZApDX1ABDl5YcPGsYDwQY5UPycDjQUgGYXIzRcmq_pAr4bsg0NU0-WJlEZRrhamxTiOIt2-y2ldVcQWK8nvP4U7gNwBGYGpJmgb_-bhxhHh5Y9yAr8788LlkTRPEwn8-SxXpcbRddyc9SWiJRY81xUgVcYZ-rjdIK0Hdy-J0pH-qxvOxR-On3e2Ck6bm71qvClmfqB6czBULFDs_sGChVJCGojOQHPHRNNgbsujuCQ1EZs4_mVM5158eP16ozL0N5JQab5skzV7P9I=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c1d00001b98d770_0%7C0a220b774c200000e29d7a94_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EOAtQo_Jsnz9XH5kW63MBNxjx7TVmqnx4WYIDdz3dShUorcSPPuF_GeCF50qJ6XzqaI8vaf1x_YZzEs30BlQvTKggdFkZK5Stx-FmqNlOeX1D_6nu_SGsHkPot7HkcVNqxVyVzkSt-h1e6XacFEz1ieXPgqVpBvaxdk6d9EsCJCzwzgVDWbYN983jlIRlEuzmb2xZLIEDSf9igWezE-UB-H7BlDgg1PgrV11tu5zWFpjqiRVHS689ksWuoD8T_ONcfOqnMlPFS1znyNvTbVrlJqwnkoNKI7nIbF-0_qFOKakOgaIjmyHTpprwU1o0QC4Pf1sR9HhsJZV-f2UQOnPDf0LPMKdtCocvA-OloUrs7cjodPgWFc1gPKRp05VGyDQI-dBYYMaj4D6FxkstJWrMe2hsp92wT14OlnMYs7INi6vb7_ZsanNiRsjT4PRq6w04rE80oQKYb7RHVL2TPDPrNMVjHtkme1vmB7CZNHOU-AJ7IH5YYjhHiJMhPDnzBKvri0FCmKWetn9WtfgP0vOEG7usklbfbZApDX1ABDl5YcPGsYDwQY5UPycDjQUgGYXIzRcmq_pAr4bsg0NU0-WJlEZRrhamxTiOIt2-y2ldVcQWK8nvP4U7gNwBGYGpJmgb_-bhxhHh5Y9yAr8788LlkTRPEwn8-SxXpcbRddyc9SWiJRY81xUgVcYZ-rjdIK0Hdy-J0pH-qxvOxR-On3e2Ck6bm71qvClmfqB6czBULFDs_sGChVJCGojOQHPHRNNgbsujuCQ1EZs4_mVM5158eP16ozL0N5JQab5skzV7P9I=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-08T14:00:00.000Z", "utc_arrival": "2023-05-08T12:00:00.000Z", "local_departure": "2023-05-08T10:40:00.000Z", "utc_departure": "2023-05-08T08:40:00.000Z"}, {"id": "0b770a224bf60000a70051c8_0|0a220b774bfa00006980c56e_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 833.433389, "distance": 1975.87, "duration": {"departure": 12600, "return": 11700, "total": 24300}, "price": 258784.1198, "conversion": {"EUR": 677.433779, "HUF": 258784.1198}, "fare": {"adults": 129392.06, "children": 129392.06, "infants": 129392.06}, "bags_price": {"1": 101.696, "2": 203.392}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 439, "hold_height": 149, "hold_length": 171, "hold_weight": 20, "hold_width": 119, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 2}, "airlines": ["W6"], "route": [{"id": "0b770a224bf60000a70051c8_0", "combination_id": "0b770a224bf60000a70051c8", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "JKREG", "fare_category": "M", "fare_classes": "J", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-03-30T21:15:00.000Z", "utc_arrival": "2023-03-30T19:15:00.000Z", "local_departure": "2023-03-30T17:45:00.000Z", "utc_departure": "2023-03-30T15:45:00.000Z"}, {"id": "0a220b774bfa00006980c56e_0", "combination_id": "0a220b774bfa00006980c56e", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "GFREG", "fare_category": "M", "fare_classes": "G", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-03T23:45:00.000Z", "utc_arrival": "2023-04-03T21:45:00.000Z", "local_departure": "2023-04-03T20:30:00.000Z", "utc_departure": "2023-04-03T18:30:00.000Z"}], "booking_token": "E-2OsR3C2YLnWvx-pd9oMAsn7ul2v5qUF2kpsWR7slcc9QpBVt6dxxnEmfcpkEH5AoK3sKSVyVgD7dcn38Neale6RlDH94JVe_fz4S9SHvkdDcs8AZ7Q1LwIz7MVIC-7bbYKKN0wwL6gvsKohKPFBcj1_gueXXn-w-F6kWzhBIjDWLRsvPYrOtTdinDAeOcVYXU72FXgntiSeXnnqAYoqt_a6n4Poo8Sltwrjzts7Qj0Z-kefwZo4-9o-4gfqOw_BnZzggllWBYs77XALQDn56OE48B3za-3GaU0WO6T0kVnNlmpvC6mAYBCbo4Nbjy0ULz5a1wjZqa2XP-mYwF7JOVP1zqkT9sAAnK9UbdOzgE2bXtp20NYtyn-bIrlRBRTBuZpE2b_8BlCH843ca8_ctW-_EmLMoleht70A2SaX3kBZty68s21p3SXCSYt2kuzUlNrDcJg7DOrbD4C1hnOWj6-JWKHsHcMslCgvDxgbT-NNSLX0FyagM6K1VRg24qwujD5EzH0wyWQkpUGvRBgtpU6pOmotxGKLCRauOQnXp6Ft9v5IV3YCq9WHeXP3_gqO4x4EnbUotTF0nrfZTVznl_7p2-08SNBLfQvsfP5d68DWNPmzulngqjtO_ATflmBEh4FzT2iGFkh2QPFUA0IeO6_S08pxRJ70G2bT7FOaTbsdsPfQ1IWNmYOY-kOQJRff1CPkisMbH5V664-zPQuK2SVZDoPxPFuKWVHf-wgJs1eV0YxIE7dPOc7HRe0mKPuQM4QzmN2Po4crk0obvIPy3ua1uTn9zi3nd-jEX512mArd_J9gktK017rpsWi5RlU_", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224bf60000a70051c8_0%7C0a220b774bfa00006980c56e_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=E-2OsR3C2YLnWvx-pd9oMAsn7ul2v5qUF2kpsWR7slcc9QpBVt6dxxnEmfcpkEH5AoK3sKSVyVgD7dcn38Neale6RlDH94JVe_fz4S9SHvkdDcs8AZ7Q1LwIz7MVIC-7bbYKKN0wwL6gvsKohKPFBcj1_gueXXn-w-F6kWzhBIjDWLRsvPYrOtTdinDAeOcVYXU72FXgntiSeXnnqAYoqt_a6n4Poo8Sltwrjzts7Qj0Z-kefwZo4-9o-4gfqOw_BnZzggllWBYs77XALQDn56OE48B3za-3GaU0WO6T0kVnNlmpvC6mAYBCbo4Nbjy0ULz5a1wjZqa2XP-mYwF7JOVP1zqkT9sAAnK9UbdOzgE2bXtp20NYtyn-bIrlRBRTBuZpE2b_8BlCH843ca8_ctW-_EmLMoleht70A2SaX3kBZty68s21p3SXCSYt2kuzUlNrDcJg7DOrbD4C1hnOWj6-JWKHsHcMslCgvDxgbT-NNSLX0FyagM6K1VRg24qwujD5EzH0wyWQkpUGvRBgtpU6pOmotxGKLCRauOQnXp6Ft9v5IV3YCq9WHeXP3_gqO4x4EnbUotTF0nrfZTVznl_7p2-08SNBLfQvsfP5d68DWNPmzulngqjtO_ATflmBEh4FzT2iGFkh2QPFUA0IeO6_S08pxRJ70G2bT7FOaTbsdsPfQ1IWNmYOY-kOQJRff1CPkisMbH5V664-zPQuK2SVZDoPxPFuKWVHf-wgJs1eV0YxIE7dPOc7HRe0mKPuQM4QzmN2Po4crk0obvIPy3ua1uTn9zi3nd-jEX512mArd_J9gktK017rpsWi5RlU_", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-03-30T21:15:00.000Z", "utc_arrival": "2023-03-30T19:15:00.000Z", "local_departure": "2023-03-30T17:45:00.000Z", "utc_departure": "2023-03-30T15:45:00.000Z"}, {"id": "0b770a224c0c00005ba10d53_0|0a220b774c0f00005b6aa57a_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 834.970631, "distance": 1975.87, "duration": {"departure": 12600, "return": 11700, "total": 24300}, "price": 259371.3562, "conversion": {"EUR": 678.971021, "HUF": 259371.3562}, "fare": {"adults": 129685.68, "children": 132528.42, "infants": 132528.42}, "bags_price": {"1": 86.688, "2": 173.376}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 439, "hold_height": 149, "hold_length": 171, "hold_weight": 20, "hold_width": 119, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 4}, "airlines": ["W6"], "route": [{"id": "0b770a224c0c00005ba10d53_0", "combination_id": "0b770a224c0c00005ba10d53", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "FREG", "fare_category": "M", "fare_classes": "F", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-21T19:45:00.000Z", "utc_arrival": "2023-04-21T17:45:00.000Z", "local_departure": "2023-04-21T16:15:00.000Z", "utc_departure": "2023-04-21T14:15:00.000Z"}, {"id": "0a220b774c0f00005b6aa57a_0", "combination_id": "0a220b774c0f00005b6aa57a", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IJREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-24T23:45:00.000Z", "utc_arrival": "2023-04-24T21:45:00.000Z", "local_departure": "2023-04-24T20:30:00.000Z", "utc_departure": "2023-04-24T18:30:00.000Z"}], "booking_token": "EZsYRTlv_WLi2npCJ-ylZ4sP_v43UyoxQhZJIjmDQtbNQNoonxcAha3Eyx__iqhYc9xYug2er_UD5Kq7g4j98-4S4BPn0Dvc2lJxcMoz5ITrcFIfPOBSay4rrHQvcbaq5lOfsy516H-Ewg3a1yBpPa0Tg_1B0ellfkzPj48dLY71rs1Vw9TII0dThXh5-xo1dElSWsYZxqI-sbczoq5v-0jYtAwTarkK0KZLJNc8X9RSorQ7BeGwEAB3Wy0OHbqgRcX1NOQ8wK7EDFck4kBKtkgXixM8ytppVVHMv7rgRvhM1xtjJqcDxfKD4oxBfeYh0ApPWxgyTBLe8Rh7w_2w-gY1gfTwhsCelAimRG088-TulJkGPUVcPRA5sCOjJVwTuSki8QaHbR_6Kmz0OmQBa2HCOjiy4wx5Q77o_zgQe__uP3TM1lIERtx_fWyR4l_jYCMnAUB_lciyp5FnZXJsqyqWizS_yKMcemD0mThCB_dtulL6ZHnCfTa4cymW3XPp6fHkVAJfRUwgpGeUZcEOA67eJ8pv0hQGihP_KH_ysNrgTtMqNv0bDeWw6-tz01W3pCdOAl9UZLP-_Bt7XQ2d02LipuPvCIHoy3xfkPIHGZud4ivDsfBYphJJL0ONNT4JCo-3plmD-4oAxp1U7fVaForL6GsIJIW5twXuYppCBGCgmd1kXkxR_k-qunDKGayrXax_4CFBcFDVgEPrSUP3jusf95slTrCVB70OpNKd6HRGPoaSjNrlzTmqkC-7hJnbh0H8BAHveQEQ6PpBTa5Djv1qazzBFDc-VfU1IbgGbffQ=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c0c00005ba10d53_0%7C0a220b774c0f00005b6aa57a_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EZsYRTlv_WLi2npCJ-ylZ4sP_v43UyoxQhZJIjmDQtbNQNoonxcAha3Eyx__iqhYc9xYug2er_UD5Kq7g4j98-4S4BPn0Dvc2lJxcMoz5ITrcFIfPOBSay4rrHQvcbaq5lOfsy516H-Ewg3a1yBpPa0Tg_1B0ellfkzPj48dLY71rs1Vw9TII0dThXh5-xo1dElSWsYZxqI-sbczoq5v-0jYtAwTarkK0KZLJNc8X9RSorQ7BeGwEAB3Wy0OHbqgRcX1NOQ8wK7EDFck4kBKtkgXixM8ytppVVHMv7rgRvhM1xtjJqcDxfKD4oxBfeYh0ApPWxgyTBLe8Rh7w_2w-gY1gfTwhsCelAimRG088-TulJkGPUVcPRA5sCOjJVwTuSki8QaHbR_6Kmz0OmQBa2HCOjiy4wx5Q77o_zgQe__uP3TM1lIERtx_fWyR4l_jYCMnAUB_lciyp5FnZXJsqyqWizS_yKMcemD0mThCB_dtulL6ZHnCfTa4cymW3XPp6fHkVAJfRUwgpGeUZcEOA67eJ8pv0hQGihP_KH_ysNrgTtMqNv0bDeWw6-tz01W3pCdOAl9UZLP-_Bt7XQ2d02LipuPvCIHoy3xfkPIHGZud4ivDsfBYphJJL0ONNT4JCo-3plmD-4oAxp1U7fVaForL6GsIJIW5twXuYppCBGCgmd1kXkxR_k-qunDKGayrXax_4CFBcFDVgEPrSUP3jusf95slTrCVB70OpNKd6HRGPoaSjNrlzTmqkC-7hJnbh0H8BAHveQEQ6PpBTa5Djv1qazzBFDc-VfU1IbgGbffQ=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-04-21T19:45:00.000Z", "utc_arrival": "2023-04-21T17:45:00.000Z", "local_departure": "2023-04-21T16:15:00.000Z", "utc_departure": "2023-04-21T14:15:00.000Z"}, {"id": "0b770a224c3800003db72594_0|0a220b774c3c00005d56eab0_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 835.199854, "distance": 1975.87, "duration": {"departure": 12600, "return": 11700, "total": 24300}, "price": 259458.9209, "conversion": {"EUR": 679.200244, "HUF": 259458.9209}, "fare": {"adults": 129729.46, "children": 135610.64, "infants": 135610.64}, "bags_price": {"1": 114.814, "2": 229.642}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 439, "hold_height": 149, "hold_length": 171, "hold_weight": 20, "hold_width": 119, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 7}, "airlines": ["W6"], "route": [{"id": "0b770a224c3800003db72594_0", "combination_id": "0b770a224c3800003db72594", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "GFREG", "fare_category": "M", "fare_classes": "G", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-04T17:05:00.000Z", "utc_arrival": "2023-06-04T15:05:00.000Z", "local_departure": "2023-06-04T13:35:00.000Z", "utc_departure": "2023-06-04T11:35:00.000Z"}, {"id": "0a220b774c3c00005d56eab0_0", "combination_id": "0a220b774c3c00005d56eab0", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-09T01:15:00.000Z", "utc_arrival": "2023-06-08T23:15:00.000Z", "local_departure": "2023-06-08T22:00:00.000Z", "utc_departure": "2023-06-08T20:00:00.000Z"}], "booking_token": "ETMb0rZ0uPqMpsk912-A_MSJ-84WXJSpz6qB6KEm-SBDB9kXvRdaN96DtejW7gRHyVsuAeJ1uOOMmGhXM_qtsT2uU_JVzdfBEdeZj1839lmWMCU9nXbVoavPeNLNZHGj50KATFiZ5G81pv-QRcfd_qcAh3IKRd0M51kFz6GRn1D4Nv4j14-0UJA9wdPNcf4dUu2ZbBz0FcarzPBayT4lHjOyef4HLc9DVp6Z1IK4ZA4BfK8tXTecZr0_T0reyJ0vIvICqgZbflz70CniGm71Y8ymQH0-k3omnaHTs3ljBSGTxL19n5uDRVkjQ1kGQbcRozYYIi2cqZ3QfB-oflqqGiK4WyWYDd9vY-vzqzwXiMeFTgQuoV8zBPsmuuHIz4A-4cYgY-lEgFjulf3WPP7DpPx_Ka56fqoeFaZ9bPq_H2Lm-u0PC0i1X4NX3TcuGs2fNBPEnUJFbprQuIchlCfZ8afRAIUodY4cOQJI3OzKJOm_N-SlOAlAU2c-sKP-0s9q5vyGTrgT-t3YJn4T7lzypfU78vtAI60mAalGpZort8jIwlIBhyCrpcIH_QUEI4V8vAhfHIFqA4_rxQRx9DTbnVj2yIUVe_aZUCGwG596LXBu-8iWsxRUfWzuSi6EtGPCTatnAiAuQ-lonMWW4IGqcC5StSXG8E00lzafTIIiBDv6gXvtB77VhjpPmsBXlrkLMyiBG0c_aFh2rpxaZFgnJHobb6JbXUfhWomu3DqerHDi6Ved4JDOQMMxM9A7VPoqI1aD9h2sAN1Wz6G2vlFE7tCwe7EspvYkV6mbMBx-Rgss=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c3800003db72594_0%7C0a220b774c3c00005d56eab0_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=ETMb0rZ0uPqMpsk912-A_MSJ-84WXJSpz6qB6KEm-SBDB9kXvRdaN96DtejW7gRHyVsuAeJ1uOOMmGhXM_qtsT2uU_JVzdfBEdeZj1839lmWMCU9nXbVoavPeNLNZHGj50KATFiZ5G81pv-QRcfd_qcAh3IKRd0M51kFz6GRn1D4Nv4j14-0UJA9wdPNcf4dUu2ZbBz0FcarzPBayT4lHjOyef4HLc9DVp6Z1IK4ZA4BfK8tXTecZr0_T0reyJ0vIvICqgZbflz70CniGm71Y8ymQH0-k3omnaHTs3ljBSGTxL19n5uDRVkjQ1kGQbcRozYYIi2cqZ3QfB-oflqqGiK4WyWYDd9vY-vzqzwXiMeFTgQuoV8zBPsmuuHIz4A-4cYgY-lEgFjulf3WPP7DpPx_Ka56fqoeFaZ9bPq_H2Lm-u0PC0i1X4NX3TcuGs2fNBPEnUJFbprQuIchlCfZ8afRAIUodY4cOQJI3OzKJOm_N-SlOAlAU2c-sKP-0s9q5vyGTrgT-t3YJn4T7lzypfU78vtAI60mAalGpZort8jIwlIBhyCrpcIH_QUEI4V8vAhfHIFqA4_rxQRx9DTbnVj2yIUVe_aZUCGwG596LXBu-8iWsxRUfWzuSi6EtGPCTatnAiAuQ-lonMWW4IGqcC5StSXG8E00lzafTIIiBDv6gXvtB77VhjpPmsBXlrkLMyiBG0c_aFh2rpxaZFgnJHobb6JbXUfhWomu3DqerHDi6Ved4JDOQMMxM9A7VPoqI1aD9h2sAN1Wz6G2vlFE7tCwe7EspvYkV6mbMBx-Rgss=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-04T17:05:00.000Z", "utc_arrival": "2023-06-04T15:05:00.000Z", "local_departure": "2023-06-04T13:35:00.000Z", "utc_departure": "2023-06-04T11:35:00.000Z"}, {"id": "0b770a224c40000061fa8349_0|0a220b774c440000824e9c86_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 834.166633, "distance": 1975.87, "duration": {"departure": 12000, "return": 11700, "total": 23700}, "price": 260082.9053, "conversion": {"EUR": 680.833683, "HUF": 260082.9053}, "fare": {"adults": 130041.45, "children": 133070.18, "infants": 133070.18}, "bags_price": {"1": 96.6, "2": 193.186}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 5}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224c40000061fa8349_0", "combination_id": "0b770a224c40000061fa8349", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-12T14:00:00.000Z", "utc_arrival": "2023-06-12T12:00:00.000Z", "local_departure": "2023-06-12T10:40:00.000Z", "utc_departure": "2023-06-12T08:40:00.000Z"}, {"id": "0a220b774c440000824e9c86_0", "combination_id": "0a220b774c440000824e9c86", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "HIREG", "fare_category": "M", "fare_classes": "H", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-16T23:45:00.000Z", "utc_arrival": "2023-06-16T21:45:00.000Z", "local_departure": "2023-06-16T20:30:00.000Z", "utc_departure": "2023-06-16T18:30:00.000Z"}], "booking_token": "EDiDbbPcZ5FbcG2zUJTdd1wkjZaqQVAuYHaNxbAxjn73fO3zxXqWXMm0IVhQG1-pYDGAuGxEyr-zxpZRMCjRjWNSfG2f3xZ_oPLB3nnCCDW0muc0e6zEO6GOH6hJwjRgU_iVTRxheLd3sX-9xTSh6dynGR2K3ED_0DtSPGy9AtgfKIxRe8zYXDpMs25Dgu5RcIHaEZGQ_6Nc7CSTM7Rk4e4U1OcPCG12rd-hpmzOANPPXFnz2hHCBjoXIM_aWi_hdlp1OwF7ADiehzUq5Ac-MKUHVigHoWnT4mHvFnZCr9YIj98nK1zXxr7LmJ_UvmF_aWtNzVaaHtjNbnp1xlcgbXsoDPnIOKqxxifiTRhYdqxfa4pHVjH9KztauSU1B9A1mSwSz0X__DLoKbAvamfRxG5BO4kwZCpAv9Eba2rSu8scZBCIyhFH5aX0WSeCyZfGb3rfrU0BUnaRtsxdDYdbIFuWhdE3fcx_bthSyEKe0djNM1BbM2kNQbt4_cTJzvbP0CA8-ulEGGWVuScqHOdGuMAPOwWFCQHp0kppmR_YGOnceiWZPyA99KWM1-8x2TmrnrvYSC0lxgQI_fKh8p8kzgth-_7yMTcwam_vsbEFGjI-IHKckBvWlVxlTkhk5yllifZGuX5Pd9_TPZuK_ZLZJlvJHMoNOVqtvx0mn1b56IKOPiff8pAgxq6QtxamF3l-LiXic9DRwRODs_uGRzOHTn-GDYYSGZk8sHGNzjz0iJDPwmX9thdAeBgzOPWwdD2J1Y01e0FkFuhNg_QiKNxh-kjyD59gYl3DPXhqmSzSRd4U=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c40000061fa8349_0%7C0a220b774c440000824e9c86_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EDiDbbPcZ5FbcG2zUJTdd1wkjZaqQVAuYHaNxbAxjn73fO3zxXqWXMm0IVhQG1-pYDGAuGxEyr-zxpZRMCjRjWNSfG2f3xZ_oPLB3nnCCDW0muc0e6zEO6GOH6hJwjRgU_iVTRxheLd3sX-9xTSh6dynGR2K3ED_0DtSPGy9AtgfKIxRe8zYXDpMs25Dgu5RcIHaEZGQ_6Nc7CSTM7Rk4e4U1OcPCG12rd-hpmzOANPPXFnz2hHCBjoXIM_aWi_hdlp1OwF7ADiehzUq5Ac-MKUHVigHoWnT4mHvFnZCr9YIj98nK1zXxr7LmJ_UvmF_aWtNzVaaHtjNbnp1xlcgbXsoDPnIOKqxxifiTRhYdqxfa4pHVjH9KztauSU1B9A1mSwSz0X__DLoKbAvamfRxG5BO4kwZCpAv9Eba2rSu8scZBCIyhFH5aX0WSeCyZfGb3rfrU0BUnaRtsxdDYdbIFuWhdE3fcx_bthSyEKe0djNM1BbM2kNQbt4_cTJzvbP0CA8-ulEGGWVuScqHOdGuMAPOwWFCQHp0kppmR_YGOnceiWZPyA99KWM1-8x2TmrnrvYSC0lxgQI_fKh8p8kzgth-_7yMTcwam_vsbEFGjI-IHKckBvWlVxlTkhk5yllifZGuX5Pd9_TPZuK_ZLZJlvJHMoNOVqtvx0mn1b56IKOPiff8pAgxq6QtxamF3l-LiXic9DRwRODs_uGRzOHTn-GDYYSGZk8sHGNzjz0iJDPwmX9thdAeBgzOPWwdD2J1Y01e0FkFuhNg_QiKNxh-kjyD59gYl3DPXhqmSzSRd4U=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-12T14:00:00.000Z", "utc_arrival": "2023-06-12T12:00:00.000Z", "local_departure": "2023-06-12T10:40:00.000Z", "utc_departure": "2023-06-12T08:40:00.000Z"}, {"id": "0b770a224c240000feaa37ef_0|0a220b774c28000046de2a57_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 847.302274, "distance": 1975.87, "duration": {"departure": 12600, "return": 12900, "total": 25500}, "price": 262044.7612, "conversion": {"EUR": 685.969344, "HUF": 262044.7612}, "fare": {"adults": 131022.38, "children": 131022.38, "infants": 131022.38}, "bags_price": {"1": 85.4, "2": 170.8}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 439, "hold_height": 149, "hold_length": 171, "hold_weight": 20, "hold_width": 119, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 2}, "airlines": ["W6"], "route": [{"id": "0b770a224c240000feaa37ef_0", "combination_id": "0b770a224c240000feaa37ef", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "FEREG", "fare_category": "M", "fare_classes": "F", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-15T19:45:00.000Z", "utc_arrival": "2023-05-15T17:45:00.000Z", "local_departure": "2023-05-15T16:15:00.000Z", "utc_departure": "2023-05-15T14:15:00.000Z"}, {"id": "0a220b774c28000046de2a57_0", "combination_id": "0a220b774c28000046de2a57", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "JKREG", "fare_category": "M", "fare_classes": "J", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-20T00:05:00.000Z", "utc_arrival": "2023-05-19T22:05:00.000Z", "local_departure": "2023-05-19T20:30:00.000Z", "utc_departure": "2023-05-19T18:30:00.000Z"}], "booking_token": "EiVBOvk-t71ehDgr_b6eCPusZCHpizIuM4qkzva_A43yvFhhvOfQkubP0xJ0MvWwRPYZhYjyWU_gPP16gNuYjm4jQsdu4AXF0sxjOm4_nYC--3KxBcjvuoyAMzybMlL4Zy0_8zV6yU69Nf3SnacjUpD8EWFmYoH3zyMqNQN7OwvPQN5_K9y9PTgamUOteG7CYQKc2hbCHElfe7s8tcJm_qfXroH8IoIXKt6HBqDnaIdWaxDvxH93XbTRtCTqZzjO8ZTq0mlUd1ikRbrqhfhP8cAd9_MxvzRdS0dizGNNkeG0u1DFs8tiQNvZagVCqI12UXIAwWMoQiRutumsv2MHSUEEqpFR0fB-GsZwROPKq_pANI8I_m1sbHIjLA8kD1kFCAa75jaVrQIyBYG1ctRF1_bwfOArm7Gb9Yv7vixIbvonMXFI4v_vWFS0yBJro5DGEjbCMHRu6Kc9y3FRm73fXHOrPMN--ue_Xag3fXd7E4mDIkcetiR4wZURFtclvOXNCQm7WRHvJHuVbt8QB_c-5LpJRYEQwj5uDGKEww8syqrFI9GanlPL00Fq09EiM2iXu4hL7rw11jPz5du-hM5HlQAXFZ3kqYJ2SLlhI1neooQey7twdCD3XhsL-SK0Thas4E1l6lJX2LBiwNUrWBTK7TZJojJB91_7WaVgMWk4wSCrVLEKfLsN0-Aj2HLUkgmq-xU4oG8zEBQdqNpSXNjNYOrZDvQdT6qvyVsl2YDS19ZJ9BNMJ1Chim5w7DtMjBkU7Aaqechum0S4iEYyjaNbZ-1dMCJy4jcmzm65KK_f23sY=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c240000feaa37ef_0%7C0a220b774c28000046de2a57_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EiVBOvk-t71ehDgr_b6eCPusZCHpizIuM4qkzva_A43yvFhhvOfQkubP0xJ0MvWwRPYZhYjyWU_gPP16gNuYjm4jQsdu4AXF0sxjOm4_nYC--3KxBcjvuoyAMzybMlL4Zy0_8zV6yU69Nf3SnacjUpD8EWFmYoH3zyMqNQN7OwvPQN5_K9y9PTgamUOteG7CYQKc2hbCHElfe7s8tcJm_qfXroH8IoIXKt6HBqDnaIdWaxDvxH93XbTRtCTqZzjO8ZTq0mlUd1ikRbrqhfhP8cAd9_MxvzRdS0dizGNNkeG0u1DFs8tiQNvZagVCqI12UXIAwWMoQiRutumsv2MHSUEEqpFR0fB-GsZwROPKq_pANI8I_m1sbHIjLA8kD1kFCAa75jaVrQIyBYG1ctRF1_bwfOArm7Gb9Yv7vixIbvonMXFI4v_vWFS0yBJro5DGEjbCMHRu6Kc9y3FRm73fXHOrPMN--ue_Xag3fXd7E4mDIkcetiR4wZURFtclvOXNCQm7WRHvJHuVbt8QB_c-5LpJRYEQwj5uDGKEww8syqrFI9GanlPL00Fq09EiM2iXu4hL7rw11jPz5du-hM5HlQAXFZ3kqYJ2SLlhI1neooQey7twdCD3XhsL-SK0Thas4E1l6lJX2LBiwNUrWBTK7TZJojJB91_7WaVgMWk4wSCrVLEKfLsN0-Aj2HLUkgmq-xU4oG8zEBQdqNpSXNjNYOrZDvQdT6qvyVsl2YDS19ZJ9BNMJ1Chim5w7DtMjBkU7Aaqechum0S4iEYyjaNbZ-1dMCJy4jcmzm65KK_f23sY=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-15T19:45:00.000Z", "utc_arrival": "2023-05-15T17:45:00.000Z", "local_departure": "2023-05-15T16:15:00.000Z", "utc_departure": "2023-05-15T14:15:00.000Z"}, {"id": "0b770a224c16000004d61df8_0|0a220b774c1a0000629e77ea_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 844.947595, "distance": 1975.87, "duration": {"departure": 12000, "return": 12900, "total": 24900}, "price": 262163.94, "conversion": {"EUR": 686.281325, "HUF": 262163.94}, "fare": {"adults": 131081.97, "children": 131081.97, "infants": 131081.97}, "bags_price": {"1": 98.77, "2": 183.288}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 3}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224c16000004d61df8_0", "combination_id": "0b770a224c16000004d61df8", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-01T14:00:00.000Z", "utc_arrival": "2023-05-01T12:00:00.000Z", "local_departure": "2023-05-01T10:40:00.000Z", "utc_departure": "2023-05-01T08:40:00.000Z"}, {"id": "0a220b774c1a0000629e77ea_0", "combination_id": "0a220b774c1a0000629e77ea", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "JREG", "fare_category": "M", "fare_classes": "J", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-06T00:05:00.000Z", "utc_arrival": "2023-05-05T22:05:00.000Z", "local_departure": "2023-05-05T20:30:00.000Z", "utc_departure": "2023-05-05T18:30:00.000Z"}], "booking_token": "EEquCnQtawcYbmDeTrvGOvVEH09AyXQMbtS0qdP6MfPEi7KlGtWIUQxItFU_SxQv4PCPiX9xHLhqufP9kVFTWCL5KqdnnZ6RBNnvdCNhyleISlJgWLo0YsnpsI5u3x3pV9X8-RHNO2TQfilTYlINA-GMKlTZgtLGKeA7ykUOryEL0oCvYnujuN15MiYLw3d0t4yU1pNr3SXO21jFwYybnqNy6n_0UImI8kozuInZ2k0dF9xw21BUrT37qVI4A_6IVTLnwhN5l9ytThctPDEq2tQGvXcjHp7PnzCy6Z4DfzblX_CdUQ-RADhRsZCMxzDZfAUJbA-o8ZserdZMA_2uPlBz4W0SY_xaaisERKBtwTPkB7pfXPzMBwaMawSBWHG3psnnz1u2WNCc6fpg6maFdB4jqVG4Mhe3nxwUcSbGrBoHL-RVz52Eae_QlCtadn0Ao0-Yd_npz4Kcy5_E5UYSPtPnin7IAesUtsQ6smJ2reSxc_Hl2ZAwJO4SNQDI4Ta-u8u48_lXE6vimBOPDqM6t_wQr4KPLtQZigiAwdP0X8ZCvxB02eK1eeWyuB4vTtNBCZ5SYCjZR5J406bZN2qcuHTYaU6X9SI9ZG7-uQ6WC9qr-aLHuDuvYz5iZ3jIYvijJSkFuoEUySyBjnby9zxCmqQPVn_PGSD_CfyodWaK4K-thj8I75QYJm-gbBlGilxwk7OXJUS2Dqo_h4VeUeyV6QIh44WOG_uDhMoe7rCCG6qqLs8EqMwD7xda9X0dMh_uy", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c16000004d61df8_0%7C0a220b774c1a0000629e77ea_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EEquCnQtawcYbmDeTrvGOvVEH09AyXQMbtS0qdP6MfPEi7KlGtWIUQxItFU_SxQv4PCPiX9xHLhqufP9kVFTWCL5KqdnnZ6RBNnvdCNhyleISlJgWLo0YsnpsI5u3x3pV9X8-RHNO2TQfilTYlINA-GMKlTZgtLGKeA7ykUOryEL0oCvYnujuN15MiYLw3d0t4yU1pNr3SXO21jFwYybnqNy6n_0UImI8kozuInZ2k0dF9xw21BUrT37qVI4A_6IVTLnwhN5l9ytThctPDEq2tQGvXcjHp7PnzCy6Z4DfzblX_CdUQ-RADhRsZCMxzDZfAUJbA-o8ZserdZMA_2uPlBz4W0SY_xaaisERKBtwTPkB7pfXPzMBwaMawSBWHG3psnnz1u2WNCc6fpg6maFdB4jqVG4Mhe3nxwUcSbGrBoHL-RVz52Eae_QlCtadn0Ao0-Yd_npz4Kcy5_E5UYSPtPnin7IAesUtsQ6smJ2reSxc_Hl2ZAwJO4SNQDI4Ta-u8u48_lXE6vimBOPDqM6t_wQr4KPLtQZigiAwdP0X8ZCvxB02eK1eeWyuB4vTtNBCZ5SYCjZR5J406bZN2qcuHTYaU6X9SI9ZG7-uQ6WC9qr-aLHuDuvYz5iZ3jIYvijJSkFuoEUySyBjnby9zxCmqQPVn_PGSD_CfyodWaK4K-thj8I75QYJm-gbBlGilxwk7OXJUS2Dqo_h4VeUeyV6QIh44WOG_uDhMoe7rCCG6qqLs8EqMwD7xda9X0dMh_uy", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-01T14:00:00.000Z", "utc_arrival": "2023-05-01T12:00:00.000Z", "local_departure": "2023-05-01T10:40:00.000Z", "utc_departure": "2023-05-01T08:40:00.000Z"}, {"id": "0b770a224beb000061734b61_0|0a220b774bef00006f39da1f_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 843.829052, "distance": 1975.87, "duration": {"departure": 12000, "return": 11700, "total": 23700}, "price": 263774.0123, "conversion": {"EUR": 690.496102, "HUF": 263774.0123}, "fare": {"adults": 131887.01, "children": 131887.01, "infants": 131887.01}, "bags_price": {"1": 90.3, "2": 180.6}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 439, "hold_height": 149, "hold_length": 171, "hold_weight": 20, "hold_width": 119, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 3}, "airlines": ["W6"], "route": [{"id": "0b770a224beb000061734b61_0", "combination_id": "0b770a224beb000061734b61", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "GHREG", "fare_category": "M", "fare_classes": "G", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-03-19T17:45:00.000Z", "utc_arrival": "2023-03-19T16:45:00.000Z", "local_departure": "2023-03-19T14:25:00.000Z", "utc_departure": "2023-03-19T13:25:00.000Z"}, {"id": "0a220b774bef00006f39da1f_0", "combination_id": "0a220b774bef00006f39da1f", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-03-24T00:05:00.000Z", "utc_arrival": "2023-03-23T23:05:00.000Z", "local_departure": "2023-03-23T20:50:00.000Z", "utc_departure": "2023-03-23T19:50:00.000Z"}], "booking_token": "Exog0sdwqUehqwDTmHKDq4Sv6z6MQZtV0nlmoYacQ7KVthfGMoCL8JSwWT1y6G2JeI7hYURbvDDB1YJ3JhXFpk15CTSUms5oohe18XtDi9CjtFjVZs55mZaMonFlz2rYkeGmT118fIaZONWxl4oMsSqzUhKasv0ZQAD_kujgAx6qPfx8akcNLSyTTcjAppi1FPJSpHs8CUcdZUgTMVnzxwOJSA8cFKD92QIMp-TrtTLqJxvY-u1-6ZWyPuyigUDZlCAhpPw8MuY-z5IBAT4kwhNanSWrktEr2eTVfVd2vn9zqBHJcJ-yiO5QMVkl-DzIB2j8_1srysSZkgu0ebn2ApQDVt5GAc1T2_EcGh70nViDlP9CkMUrjczFhjQRiTUbFFccp18nA4ysCZ-tBREszcNl79I8cWB4GlBksuIgS_ej5IQ00kVNISHiU1JFMJqSlO2r2eK6dXT3AW1OADWxlnWQYSQ74VZVS6PmaeuJy0Gkm0G-dMfMZOquUhehztd_CENJe3QjP9fEr7pFzBYpA9OemcpF8MVwj7GcxmRI6X-5i6qcoB9yTxfp7ssBkp3hwQf9Vkw5W6wGRhsR_kd22l9d8LSydFev1VG4l2GVTVn1LQrP14cyckR5kUjeit695Y4ylTMLWzd5mZgCvEYAK6_AfcZdZWRtJnaLmtUflR48Jb12_l-OOACyr6U38RhgSFDwdRpCI_gco6eFPnV0M_uIekfXu8XFS8IbujGWzToSw8cnfQFSmcFgk0SVHNb4n9ybsXmBTi5Ld17J96-j7s3kIhyiIHeZ6ZJ_CnE807l4=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224beb000061734b61_0%7C0a220b774bef00006f39da1f_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=Exog0sdwqUehqwDTmHKDq4Sv6z6MQZtV0nlmoYacQ7KVthfGMoCL8JSwWT1y6G2JeI7hYURbvDDB1YJ3JhXFpk15CTSUms5oohe18XtDi9CjtFjVZs55mZaMonFlz2rYkeGmT118fIaZONWxl4oMsSqzUhKasv0ZQAD_kujgAx6qPfx8akcNLSyTTcjAppi1FPJSpHs8CUcdZUgTMVnzxwOJSA8cFKD92QIMp-TrtTLqJxvY-u1-6ZWyPuyigUDZlCAhpPw8MuY-z5IBAT4kwhNanSWrktEr2eTVfVd2vn9zqBHJcJ-yiO5QMVkl-DzIB2j8_1srysSZkgu0ebn2ApQDVt5GAc1T2_EcGh70nViDlP9CkMUrjczFhjQRiTUbFFccp18nA4ysCZ-tBREszcNl79I8cWB4GlBksuIgS_ej5IQ00kVNISHiU1JFMJqSlO2r2eK6dXT3AW1OADWxlnWQYSQ74VZVS6PmaeuJy0Gkm0G-dMfMZOquUhehztd_CENJe3QjP9fEr7pFzBYpA9OemcpF8MVwj7GcxmRI6X-5i6qcoB9yTxfp7ssBkp3hwQf9Vkw5W6wGRhsR_kd22l9d8LSydFev1VG4l2GVTVn1LQrP14cyckR5kUjeit695Y4ylTMLWzd5mZgCvEYAK6_AfcZdZWRtJnaLmtUflR48Jb12_l-OOACyr6U38RhgSFDwdRpCI_gco6eFPnV0M_uIekfXu8XFS8IbujGWzToSw8cnfQFSmcFgk0SVHNb4n9ybsXmBTi5Ld17J96-j7s3kIhyiIHeZ6ZJ_CnE807l4=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-03-19T17:45:00.000Z", "utc_arrival": "2023-03-19T16:45:00.000Z", "local_departure": "2023-03-19T14:25:00.000Z", "utc_departure": "2023-03-19T13:25:00.000Z"}, {"id": "0b770a224c4b00004d10476b_0|0a220b774c4e00006fcb60de_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 845.479777, "distance": 1975.87, "duration": {"departure": 12600, "return": 11400, "total": 24000}, "price": 263895.2593, "conversion": {"EUR": 690.813497, "HUF": 263895.2593}, "fare": {"adults": 131947.63, "children": 131947.63, "infants": 131947.63}, "bags_price": {"1": 104.524, "2": 218.834}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 158, "hold_height": 52, "hold_length": 78, "hold_weight": 20, "hold_width": 28, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 3, "personal_item_width": 15}, "availability": {"seats": 5}, "airlines": ["W6", "IB"], "route": [{"id": "0b770a224c4b00004d10476b_0", "combination_id": "0b770a224c4b00004d10476b", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IJREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-23T19:45:00.000Z", "utc_arrival": "2023-06-23T17:45:00.000Z", "local_departure": "2023-06-23T16:15:00.000Z", "utc_departure": "2023-06-23T14:15:00.000Z"}, {"id": "0a220b774c4e00006fcb60de_0", "combination_id": "0a220b774c4e00006fcb60de", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "IB", "flight_no": 3278, "operating_carrier": "IB", "operating_flight_no": "3278", "fare_basis": "SDNNAOB4", "fare_category": "M", "fare_classes": "S", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-26T14:55:00.000Z", "utc_arrival": "2023-06-26T12:55:00.000Z", "local_departure": "2023-06-26T11:45:00.000Z", "utc_departure": "2023-06-26T09:45:00.000Z"}], "booking_token": "EW7aCKWUsooa9R2mYO5SqcbUyhUOZAq-fvDSKg2AM4ELbWXVKz-hg_eu3aucankFRIK45c_1Za47RHkiRda8yCPndG-dUxEZH1N__Gq_I6Z2vNJNnsbmqYYd4ARUx7VTmBej8dMQsfkdISETrimKIioeYsPf_iNbyHe1NjEuYOuQDa4Kt0aGoPa8eWGG5GegeNRZsMU1JR2h5CBhoiMofOSCeEnRQ42z665xv3ulEgM7eb7OvLLbeB280Kuf7zX0-EEu60U1lC3uaDtB4nYh1CbuPeqxPBcRK37SfWUuZxeuJknW_7LqhsH_DEf-gALohESf_IIW8JsVWrAiqX-VjYfglO_xoAGM4bDbfUG460XOXS6g0GXWVH43Tpsnx8h46Y8pQiM5XqfgokD6IynbB9VKjnwOT0zbbV5KGE2-M5OKIl0CMC3GrKfmPtgfTlviO-7qKGmVQpirwYg-7HtoEA_8tWPVXoGSsC6uR4pPyjp_TgAVbP_oUorB3TfOJAbeWWXXfHvgu0HdFpM5E3IjjE6RpTjtDm6YAEwpsA-XuTls8yYYOxw3LBi74qr9Ekymhs5JhigljHfpQTc5fm5opBf6b-FqUAYPxR1pMl9mZDsSvBHy8ArkfUsWR7auxkwxfju8WmGMzs2zPMixrYWUEQaK__nVYWIW8aMtuZfUU0t47noyDC2Bxe90ehvZLxL6Kja-ltzb9yXz_6rw3QdkYwk7Z9ouwup9h74saAS9mrp9EeZDD-vmSoLnr_tIOOc2_GeDedOYiFwMp3YUMF4JWQlckv0pvJAkMCqpcxJrOx_DMuJ8Urd3MZWZv_9GCS2-5", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c4b00004d10476b_0%7C0a220b774c4e00006fcb60de_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EW7aCKWUsooa9R2mYO5SqcbUyhUOZAq-fvDSKg2AM4ELbWXVKz-hg_eu3aucankFRIK45c_1Za47RHkiRda8yCPndG-dUxEZH1N__Gq_I6Z2vNJNnsbmqYYd4ARUx7VTmBej8dMQsfkdISETrimKIioeYsPf_iNbyHe1NjEuYOuQDa4Kt0aGoPa8eWGG5GegeNRZsMU1JR2h5CBhoiMofOSCeEnRQ42z665xv3ulEgM7eb7OvLLbeB280Kuf7zX0-EEu60U1lC3uaDtB4nYh1CbuPeqxPBcRK37SfWUuZxeuJknW_7LqhsH_DEf-gALohESf_IIW8JsVWrAiqX-VjYfglO_xoAGM4bDbfUG460XOXS6g0GXWVH43Tpsnx8h46Y8pQiM5XqfgokD6IynbB9VKjnwOT0zbbV5KGE2-M5OKIl0CMC3GrKfmPtgfTlviO-7qKGmVQpirwYg-7HtoEA_8tWPVXoGSsC6uR4pPyjp_TgAVbP_oUorB3TfOJAbeWWXXfHvgu0HdFpM5E3IjjE6RpTjtDm6YAEwpsA-XuTls8yYYOxw3LBi74qr9Ekymhs5JhigljHfpQTc5fm5opBf6b-FqUAYPxR1pMl9mZDsSvBHy8ArkfUsWR7auxkwxfju8WmGMzs2zPMixrYWUEQaK__nVYWIW8aMtuZfUU0t47noyDC2Bxe90ehvZLxL6Kja-ltzb9yXz_6rw3QdkYwk7Z9ouwup9h74saAS9mrp9EeZDD-vmSoLnr_tIOOc2_GeDedOYiFwMp3YUMF4JWQlckv0pvJAkMCqpcxJrOx_DMuJ8Urd3MZWZv_9GCS2-5", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-23T19:45:00.000Z", "utc_arrival": "2023-06-23T17:45:00.000Z", "local_departure": "2023-06-23T16:15:00.000Z", "utc_departure": "2023-06-23T14:15:00.000Z"}, {"id": "0b770a224c0800004ab681ca_0|0a220b774c0c0000c53091b6_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 850.781912, "distance": 1975.87, "duration": {"departure": 12000, "return": 12900, "total": 24900}, "price": 264392.6871, "conversion": {"EUR": 692.115642, "HUF": 264392.6871}, "fare": {"adults": 132196.34, "children": 135205.46, "infants": 135205.46}, "bags_price": {"1": 90.706, "2": 181.412}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 6}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224c0800004ab681ca_0", "combination_id": "0b770a224c0800004ab681ca", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-17T14:00:00.000Z", "utc_arrival": "2023-04-17T12:00:00.000Z", "local_departure": "2023-04-17T10:40:00.000Z", "utc_departure": "2023-04-17T08:40:00.000Z"}, {"id": "0a220b774c0c0000c53091b6_0", "combination_id": "0a220b774c0c0000c53091b6", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IJREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-22T00:05:00.000Z", "utc_arrival": "2023-04-21T22:05:00.000Z", "local_departure": "2023-04-21T20:30:00.000Z", "utc_departure": "2023-04-21T18:30:00.000Z"}], "booking_token": "ELB85S9o9IXAAIsBoST_-AzMFPHOuShqoJKKVlWwFMWEmP9OWGdPB7wZGfuLHCEZe0SyUX_nuc2K1W8AFeTycJ49ZzTKDRBIBiviaoi3oPaSbCbTBLenkgsnzXX6RSOcANNOj58nipcNr4t1uwtO5wXCRP1SvK_D8YW3ui8ABCHzrqaC6C40xr29IdqwlAE_RLehjlFJBI5QEtN-gfkitHcUKL0CGp9W0AWDZaAWhLuhnsYi11B1nVuTILdczjeuTlhBmOpoRbAN5YJJGpK-WzLXelvFDvC8He417ESaxYbf6eFBmA5h01UbY8hp3yASjBUZdlkByGSKuYey1oms_S6-EJ4scqM0NJrH0SDW8w4SXNe_EbV9SGH-NiK6KDPVT5_W9WRwrl0UjJsIGm1AcQ9fRFC-EXShxYtBw4No-7y60KeereVEvqQxGyQDCe-U8xhmX20ao_ti0y9f2TNRnAbmssKDNm7NEmrDF6W4xwBjQu08AIiZMx0wVJlFUTMYs-W3-NpOIqNbix_4Fe6o-95PeewNj_yVGI4L1eBUj94jYmnr7l3raUb8eCAw-k3fpbevseZoslUXG_tH8ggkFwL_hOosn_PZkm2eKoV1YkIx4yLJBznf53zRFXz50EvTNcjIx3XoX9wPqEkXFaAbE4QZUJ4H1xPs-v2yBKH9RlCxYqhOXqMTavF5WlYn_FqATGCG0pIiDBRYwuSz959nxMm16pyRwjyXQwKf6Vs1Rz4RYzDZLk0RHf7nPe2UdFFiR1Xn_be8cDbN2T_pkfwrruxxJ0yDQE219c7mfaLZYztI=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c0800004ab681ca_0%7C0a220b774c0c0000c53091b6_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=ELB85S9o9IXAAIsBoST_-AzMFPHOuShqoJKKVlWwFMWEmP9OWGdPB7wZGfuLHCEZe0SyUX_nuc2K1W8AFeTycJ49ZzTKDRBIBiviaoi3oPaSbCbTBLenkgsnzXX6RSOcANNOj58nipcNr4t1uwtO5wXCRP1SvK_D8YW3ui8ABCHzrqaC6C40xr29IdqwlAE_RLehjlFJBI5QEtN-gfkitHcUKL0CGp9W0AWDZaAWhLuhnsYi11B1nVuTILdczjeuTlhBmOpoRbAN5YJJGpK-WzLXelvFDvC8He417ESaxYbf6eFBmA5h01UbY8hp3yASjBUZdlkByGSKuYey1oms_S6-EJ4scqM0NJrH0SDW8w4SXNe_EbV9SGH-NiK6KDPVT5_W9WRwrl0UjJsIGm1AcQ9fRFC-EXShxYtBw4No-7y60KeereVEvqQxGyQDCe-U8xhmX20ao_ti0y9f2TNRnAbmssKDNm7NEmrDF6W4xwBjQu08AIiZMx0wVJlFUTMYs-W3-NpOIqNbix_4Fe6o-95PeewNj_yVGI4L1eBUj94jYmnr7l3raUb8eCAw-k3fpbevseZoslUXG_tH8ggkFwL_hOosn_PZkm2eKoV1YkIx4yLJBznf53zRFXz50EvTNcjIx3XoX9wPqEkXFaAbE4QZUJ4H1xPs-v2yBKH9RlCxYqhOXqMTavF5WlYn_FqATGCG0pIiDBRYwuSz959nxMm16pyRwjyXQwKf6Vs1Rz4RYzDZLk0RHf7nPe2UdFFiR1Xn_be8cDbN2T_pkfwrruxxJ0yDQE219c7mfaLZYztI=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-04-17T14:00:00.000Z", "utc_arrival": "2023-04-17T12:00:00.000Z", "local_departure": "2023-04-17T10:40:00.000Z", "utc_departure": "2023-04-17T08:40:00.000Z"}, {"id": "0b770a224c0f0000c5fb399f_0|0a220b774c1200004e293ac3_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 848.317386, "distance": 1975.87, "duration": {"departure": 12600, "return": 11700, "total": 24300}, "price": 264469.9037, "conversion": {"EUR": 692.317776, "HUF": 264469.9037}, "fare": {"adults": 132234.95, "children": 132234.95, "infants": 132234.95}, "bags_price": {"1": 118.02, "2": 236.04}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 439, "hold_height": 149, "hold_length": 171, "hold_weight": 20, "hold_width": 119, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 2}, "airlines": ["W6"], "route": [{"id": "0b770a224c0f0000c5fb399f_0", "combination_id": "0b770a224c0f0000c5fb399f", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IJREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-24T19:45:00.000Z", "utc_arrival": "2023-04-24T17:45:00.000Z", "local_departure": "2023-04-24T16:15:00.000Z", "utc_departure": "2023-04-24T14:15:00.000Z"}, {"id": "0a220b774c1200004e293ac3_0", "combination_id": "0a220b774c1200004e293ac3", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "GFREG", "fare_category": "M", "fare_classes": "G", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-28T01:15:00.000Z", "utc_arrival": "2023-04-27T23:15:00.000Z", "local_departure": "2023-04-27T22:00:00.000Z", "utc_departure": "2023-04-27T20:00:00.000Z"}], "booking_token": "EwhzIhSbP4gorq8HLBtZC5Va38LDPjnJUekC8OTSbAlYMsjxjeWgtm2PMdHaNmmXL9IVjfzs1E2LRnyawFiHXWRssv_BnvlZBtQ6LwR-zgmHVqnnNMCmq_V7YXPsRMqA2GnzZJ1NX2jF_TNPsYQqiWYdoa-esU9ztr-BDdKmqkxrzbgkje-LJnJEpYdxQkzP0MnqgA6ZMeyDhU5tTNFtb4pX69HU1pSG5jAijsERWfrdpMqvkZUnQCKZmaDNrB4umsk-N-tQ7HybNQbr69oU9IIyMCKJ3UMbFWkjwSkYgKzQgLiMCUtxbF2i1em8db-Wxrm59SSQMDxD93kQhYjGmU3KNb7EWE22CoxgwBQkk-0DM1Y6PgZNaN3hyR0ANmFad35vK8TGODhYut9NdwNudGfwWnjO20P3MMjTgPfbel8DjawGW5W5FhJFqHlfP16Z0XtNscdUAyOBhwzleN-fJOv9jkgxWwkz_yBIDKm_vK7UZbqq46n5ETXaR2fxi4CUwGOkCiayk3N6sbtEYqirSP2J6d3F9yDXwMLwMCwCKLLG93gXYW-Hb_1DJoxzKeRWsIIdzuXlPWAX8-Mzsdgu0rFspU06XEoTNP-BpwQCQCompdlKmIzPCGeo_NSB6PgJOG44SV1xSafPoZO9cz-Tl4rC3k6Jlo9tC2tVFdhcc_SDQw_uIbSbFuA_8hcOCHnE4MOmWj-Kl56-S6pH9NnpbXjS6KHct5C28dGE2K2fbXl3Wih1y2SYTdqPFtbDMPque71oMXNiWOXkrDUEkYHGN22MUjsCd5xtLb2yy6_A3shE=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c0f0000c5fb399f_0%7C0a220b774c1200004e293ac3_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EwhzIhSbP4gorq8HLBtZC5Va38LDPjnJUekC8OTSbAlYMsjxjeWgtm2PMdHaNmmXL9IVjfzs1E2LRnyawFiHXWRssv_BnvlZBtQ6LwR-zgmHVqnnNMCmq_V7YXPsRMqA2GnzZJ1NX2jF_TNPsYQqiWYdoa-esU9ztr-BDdKmqkxrzbgkje-LJnJEpYdxQkzP0MnqgA6ZMeyDhU5tTNFtb4pX69HU1pSG5jAijsERWfrdpMqvkZUnQCKZmaDNrB4umsk-N-tQ7HybNQbr69oU9IIyMCKJ3UMbFWkjwSkYgKzQgLiMCUtxbF2i1em8db-Wxrm59SSQMDxD93kQhYjGmU3KNb7EWE22CoxgwBQkk-0DM1Y6PgZNaN3hyR0ANmFad35vK8TGODhYut9NdwNudGfwWnjO20P3MMjTgPfbel8DjawGW5W5FhJFqHlfP16Z0XtNscdUAyOBhwzleN-fJOv9jkgxWwkz_yBIDKm_vK7UZbqq46n5ETXaR2fxi4CUwGOkCiayk3N6sbtEYqirSP2J6d3F9yDXwMLwMCwCKLLG93gXYW-Hb_1DJoxzKeRWsIIdzuXlPWAX8-Mzsdgu0rFspU06XEoTNP-BpwQCQCompdlKmIzPCGeo_NSB6PgJOG44SV1xSafPoZO9cz-Tl4rC3k6Jlo9tC2tVFdhcc_SDQw_uIbSbFuA_8hcOCHnE4MOmWj-Kl56-S6pH9NnpbXjS6KHct5C28dGE2K2fbXl3Wih1y2SYTdqPFtbDMPque71oMXNiWOXkrDUEkYHGN22MUjsCd5xtLb2yy6_A3shE=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-04-24T19:45:00.000Z", "utc_arrival": "2023-04-24T17:45:00.000Z", "local_departure": "2023-04-24T16:15:00.000Z", "utc_departure": "2023-04-24T14:15:00.000Z"}, {"id": "0b770a224c0800005e1413f9_0|0a220b774c0c00003f9c62a9_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 847.613745, "distance": 1975.87, "duration": {"departure": 12600, "return": 11400, "total": 24000}, "price": 264710.449, "conversion": {"EUR": 692.947465, "HUF": 264710.449}, "fare": {"adults": 132355.22, "children": 132355.22, "infants": 132355.22}, "bags_price": {"1": 102.41, "2": 204.806}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 3}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224c0800005e1413f9_0", "combination_id": "0b770a224c0800005e1413f9", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "JREG", "fare_category": "M", "fare_classes": "J", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-17T19:45:00.000Z", "utc_arrival": "2023-04-17T17:45:00.000Z", "local_departure": "2023-04-17T16:15:00.000Z", "utc_departure": "2023-04-17T14:15:00.000Z"}, {"id": "0a220b774c0c00003f9c62a9_0", "combination_id": "0a220b774c0c00003f9c62a9", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-21T18:00:00.000Z", "utc_arrival": "2023-04-21T16:00:00.000Z", "local_departure": "2023-04-21T14:50:00.000Z", "utc_departure": "2023-04-21T12:50:00.000Z"}], "booking_token": "EAKtM1JrWWntmZ5iBEZ-Q9oy0HnoKfp0_s0d_v33RNtlUw4PjWiGbYqr1LUlMjus-DzDjHToariXF95JifO5KirCdCw0bmYVnjqeIxgMb7hcdyq1lD4q2CGoF6zizL-NU2i3Vi9LuD66UHGjhp0fUxskbUr5vH2tu6BojfOteic1qvD_m48phDlQCIR9tpD7ojvOylP9hrPj-eSG-Dezaijea2iBbDxOrIVAlzAia4vFQYvLJ8pE__X60iVqKp9Vl2vKw0FaZ8YZJR_588_0Cqicrq1GUvS2lDdKPZw-mqnlyRhaepg6dQW9Wjxc6S5EGlFmHoNdUw5k41EGUKQM8jMi2zW0kn1pxMv2fXE94HguAmbkqxQrHtqeVzWCGGBgNbM2LLQw9hhzxvB65lApqJEcHuW63fNFyWr6CdbCEhUwQOIBf4Gqxgl99ECvU99NVbQy0BRzIWspEByC__joesI6me7Z5sI6NJmTtxojwy4-Ow4OBiK_WPKKZ6EGtjQ53HQlGf7pa594QAKVXeR_XzmymFLj6eeKpD_wSYbr6lgyWwKhVGC96OHgvoIl2bz_gDR9t1kADBZkB7fzf9yDSLrmrYdzZICn9bwt42beMbJf00HgGygZBKvxDIsyQ8qvgPXQZh2AT7AcKC1gU3DtV5Bg0r6EeGvEqsTg8seUSVCAox6zMpNk7kHFuVLedzjmVlxvLSmkAfPjDzlFIAihNh_Q8bvSZsnVZ3UOw4774iSvK0E9H-Ubnt1j1Psr62P3QheFAtOXNc3nG5TwqUWpjMQ==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c0800005e1413f9_0%7C0a220b774c0c00003f9c62a9_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EAKtM1JrWWntmZ5iBEZ-Q9oy0HnoKfp0_s0d_v33RNtlUw4PjWiGbYqr1LUlMjus-DzDjHToariXF95JifO5KirCdCw0bmYVnjqeIxgMb7hcdyq1lD4q2CGoF6zizL-NU2i3Vi9LuD66UHGjhp0fUxskbUr5vH2tu6BojfOteic1qvD_m48phDlQCIR9tpD7ojvOylP9hrPj-eSG-Dezaijea2iBbDxOrIVAlzAia4vFQYvLJ8pE__X60iVqKp9Vl2vKw0FaZ8YZJR_588_0Cqicrq1GUvS2lDdKPZw-mqnlyRhaepg6dQW9Wjxc6S5EGlFmHoNdUw5k41EGUKQM8jMi2zW0kn1pxMv2fXE94HguAmbkqxQrHtqeVzWCGGBgNbM2LLQw9hhzxvB65lApqJEcHuW63fNFyWr6CdbCEhUwQOIBf4Gqxgl99ECvU99NVbQy0BRzIWspEByC__joesI6me7Z5sI6NJmTtxojwy4-Ow4OBiK_WPKKZ6EGtjQ53HQlGf7pa594QAKVXeR_XzmymFLj6eeKpD_wSYbr6lgyWwKhVGC96OHgvoIl2bz_gDR9t1kADBZkB7fzf9yDSLrmrYdzZICn9bwt42beMbJf00HgGygZBKvxDIsyQ8qvgPXQZh2AT7AcKC1gU3DtV5Bg0r6EeGvEqsTg8seUSVCAox6zMpNk7kHFuVLedzjmVlxvLSmkAfPjDzlFIAihNh_Q8bvSZsnVZ3UOw4774iSvK0E9H-Ubnt1j1Psr62P3QheFAtOXNc3nG5TwqUWpjMQ==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-04-17T19:45:00.000Z", "utc_arrival": "2023-04-17T17:45:00.000Z", "local_departure": "2023-04-17T16:15:00.000Z", "utc_departure": "2023-04-17T14:15:00.000Z"}, {"id": "0b770a224c4400001cdf0063_0|0a220b774c470000d863fde0_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 848.636792, "distance": 1975.87, "duration": {"departure": 12600, "return": 11400, "total": 24000}, "price": 265101.2596, "conversion": {"EUR": 693.970512, "HUF": 265101.2596}, "fare": {"adults": 132550.63, "children": 135162.39, "infants": 135162.39}, "bags_price": {"1": 72.268, "2": 154.336}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 158, "hold_height": 52, "hold_length": 78, "hold_weight": 20, "hold_width": 28, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 3, "personal_item_width": 15}, "availability": {"seats": 7}, "airlines": ["W6", "IB"], "route": [{"id": "0b770a224c4400001cdf0063_0", "combination_id": "0b770a224c4400001cdf0063", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "HIREG", "fare_category": "M", "fare_classes": "H", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-16T19:45:00.000Z", "utc_arrival": "2023-06-16T17:45:00.000Z", "local_departure": "2023-06-16T16:15:00.000Z", "utc_departure": "2023-06-16T14:15:00.000Z"}, {"id": "0a220b774c470000d863fde0_0", "combination_id": "0a220b774c470000d863fde0", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "IB", "flight_no": 3278, "operating_carrier": "IB", "operating_flight_no": "3278", "fare_basis": "SWNNAOB4", "fare_category": "M", "fare_classes": "S", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-19T14:55:00.000Z", "utc_arrival": "2023-06-19T12:55:00.000Z", "local_departure": "2023-06-19T11:45:00.000Z", "utc_departure": "2023-06-19T09:45:00.000Z"}], "booking_token": "EuyHvW6JY6Vf-MkPL89MPW_1uEa1oX5ygAWDhzM7hrJZmbrQDxMAb33KY_hz6Ze-zFJQsu_0roO8EIodFBFYqxd1faInCHOZV4agQpxz8IS4aFaahEcbys60DvxfQfTDp0QRjHSvR3zhxtzVHLfbFG5XLxgAuZyM1QN3nJW447JmiEgMxnTKj1hBGpwfw-c_QeETTKEoT0FPjMUxs0t5ZK7K0n56ZDdkDQXlQZPxtSSjxN9u5EVOnv9sYWAdGTfN1IBlRoiqb14MEeqxLAVj_3MQT_AwuFE4r3bUkFbuGgiUMkP8ua_A-CJx_iLQjrr01VD3NAiXhkyv2g4lqljmJyuwextuNsM120tcjtFs-9Ss4t95bGtuwJWwz87WXPm8aZ2H-GartnjvIIkC52t4NwoRQ6OcNTowxWWaHuiuvR_ouaOqjwddNNjjvxuroMfCLy74IFL65ukHI6KiF0n3x2o0nrIiYQkKb90V4It2iXxdo8dUuiuC32bCYz42Ckox1z_KLuqnnrVf0TGQo4V3yfPqXFwYymbsq3kxqTZ4EfvcoVBMqYx4xdggcV0oeQ8HINJEBMkL4RjQEar5r82vM6gvm9QNrdpRTx6coT-i8CYi-VNnWW9-3FM0uxLXk1x4qt0ezd1rstYtNtBJXJS--Jp_k0KbJCPgQzAtEQ5Uq7-HNqGZes0SO-F_mxeUqu9Viau3ZAcDaDjVV8-r_mSqbMze3F_-QUUZXcDUSnVMME3bLf_V5QoN-XwOfbGEOFtlsJEgKzcTf5HTZXN39eRlyNTk4vuD1JUVNeF5MeyLhreHYskHDHiDhmdu6hq9u0-ih", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c4400001cdf0063_0%7C0a220b774c470000d863fde0_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EuyHvW6JY6Vf-MkPL89MPW_1uEa1oX5ygAWDhzM7hrJZmbrQDxMAb33KY_hz6Ze-zFJQsu_0roO8EIodFBFYqxd1faInCHOZV4agQpxz8IS4aFaahEcbys60DvxfQfTDp0QRjHSvR3zhxtzVHLfbFG5XLxgAuZyM1QN3nJW447JmiEgMxnTKj1hBGpwfw-c_QeETTKEoT0FPjMUxs0t5ZK7K0n56ZDdkDQXlQZPxtSSjxN9u5EVOnv9sYWAdGTfN1IBlRoiqb14MEeqxLAVj_3MQT_AwuFE4r3bUkFbuGgiUMkP8ua_A-CJx_iLQjrr01VD3NAiXhkyv2g4lqljmJyuwextuNsM120tcjtFs-9Ss4t95bGtuwJWwz87WXPm8aZ2H-GartnjvIIkC52t4NwoRQ6OcNTowxWWaHuiuvR_ouaOqjwddNNjjvxuroMfCLy74IFL65ukHI6KiF0n3x2o0nrIiYQkKb90V4It2iXxdo8dUuiuC32bCYz42Ckox1z_KLuqnnrVf0TGQo4V3yfPqXFwYymbsq3kxqTZ4EfvcoVBMqYx4xdggcV0oeQ8HINJEBMkL4RjQEar5r82vM6gvm9QNrdpRTx6coT-i8CYi-VNnWW9-3FM0uxLXk1x4qt0ezd1rstYtNtBJXJS--Jp_k0KbJCPgQzAtEQ5Uq7-HNqGZes0SO-F_mxeUqu9Viau3ZAcDaDjVV8-r_mSqbMze3F_-QUUZXcDUSnVMME3bLf_V5QoN-XwOfbGEOFtlsJEgKzcTf5HTZXN39eRlyNTk4vuD1JUVNeF5MeyLhreHYskHDHiDhmdu6hq9u0-ih", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-16T19:45:00.000Z", "utc_arrival": "2023-06-16T17:45:00.000Z", "local_departure": "2023-06-16T16:15:00.000Z", "utc_departure": "2023-06-16T14:15:00.000Z"}, {"id": "0b770a224c4000007558117a_0|0a220b774c440000824e9c86_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 850.643656, "distance": 1975.87, "duration": {"departure": 12600, "return": 11700, "total": 24300}, "price": 265358.554, "conversion": {"EUR": 694.644046, "HUF": 265358.554}, "fare": {"adults": 132679.28, "children": 135879.92, "infants": 135879.92}, "bags_price": {"1": 118.846, "2": 237.706}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 439, "hold_height": 149, "hold_length": 171, "hold_weight": 20, "hold_width": 119, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 3}, "airlines": ["W6"], "route": [{"id": "0b770a224c4000007558117a_0", "combination_id": "0b770a224c4000007558117a", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "HREG", "fare_category": "M", "fare_classes": "H", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-12T19:45:00.000Z", "utc_arrival": "2023-06-12T17:45:00.000Z", "local_departure": "2023-06-12T16:15:00.000Z", "utc_departure": "2023-06-12T14:15:00.000Z"}, {"id": "0a220b774c440000824e9c86_0", "combination_id": "0a220b774c440000824e9c86", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "HIREG", "fare_category": "M", "fare_classes": "H", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-16T23:45:00.000Z", "utc_arrival": "2023-06-16T21:45:00.000Z", "local_departure": "2023-06-16T20:30:00.000Z", "utc_departure": "2023-06-16T18:30:00.000Z"}], "booking_token": "ET8ePf5dVFYIwlr85cigmnuP1j0r97NVP-4X3HLvU-XwOtBAWRDjhJXGGI6gyw9FFWL2flQmcwS04Ydzisxd7xfyFa_tQnaJ7q8P-McDMYDX2W-N9rtnwBdX1M5LD0RDpGJRZAVZ3YZosre_kSiS9udBtBFLfaKDD5YjZ3h3VQIjFdqlutbiw-lpv3F3ya5wq_CT252uXLBd3qE7D_mBdVPGeVr9Y4Nm0UIBfLgxR54H5kZX-NN8vgZp9rc-f1AjixZuFLhIS0-FYCftwMFCzE-NBkpvZ4hAMAjKqf2wxipN1Q0XXNtpoouodDnkcz8an5943f-9VgjWodWfJtB80bVgZzdk1J5GX1LAHfAAfHcaFNXTcObKu3kgt6xL_kcRhXqCUnPY7J2r0c_MAcBL3oWnseEPmVu1eAG5Aoi06MF_YigM9Fh05zOBnu56r7_vqk8lS_NQ4YFdDfc5_xIT1YvAWQrvlSf47WDZrfrElSfleJ1NqP9VsX8BD0JkiU4oYxij4aGd0RL7HJcSFph4hKOSFdSgw56_jnEnpLGMUeuWodwWjW-2tfgb4H8aDbgq4a9Ma2NJo1jWZuaSUe4J1RjP6M3D9xUPQdrbTurfE4MGY9t9w2hqz4tG9KSVbaSwZqf8QDek-uuSRYwDX3NeRFMT49UKvM44_zMFxOUqOcl1bBuJ6GnaR9D_a2dQ3WHcvqw3FhsmEYvghmcoYFysZpPirk3aneGjS6ztx56-AXRCgVdEtf32JdP3kTOe1QwifJQ_w4KK0MJCsR2z0gK-lTYWMa1zgs2PreTo8_mHAfTo=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c4000007558117a_0%7C0a220b774c440000824e9c86_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=ET8ePf5dVFYIwlr85cigmnuP1j0r97NVP-4X3HLvU-XwOtBAWRDjhJXGGI6gyw9FFWL2flQmcwS04Ydzisxd7xfyFa_tQnaJ7q8P-McDMYDX2W-N9rtnwBdX1M5LD0RDpGJRZAVZ3YZosre_kSiS9udBtBFLfaKDD5YjZ3h3VQIjFdqlutbiw-lpv3F3ya5wq_CT252uXLBd3qE7D_mBdVPGeVr9Y4Nm0UIBfLgxR54H5kZX-NN8vgZp9rc-f1AjixZuFLhIS0-FYCftwMFCzE-NBkpvZ4hAMAjKqf2wxipN1Q0XXNtpoouodDnkcz8an5943f-9VgjWodWfJtB80bVgZzdk1J5GX1LAHfAAfHcaFNXTcObKu3kgt6xL_kcRhXqCUnPY7J2r0c_MAcBL3oWnseEPmVu1eAG5Aoi06MF_YigM9Fh05zOBnu56r7_vqk8lS_NQ4YFdDfc5_xIT1YvAWQrvlSf47WDZrfrElSfleJ1NqP9VsX8BD0JkiU4oYxij4aGd0RL7HJcSFph4hKOSFdSgw56_jnEnpLGMUeuWodwWjW-2tfgb4H8aDbgq4a9Ma2NJo1jWZuaSUe4J1RjP6M3D9xUPQdrbTurfE4MGY9t9w2hqz4tG9KSVbaSwZqf8QDek-uuSRYwDX3NeRFMT49UKvM44_zMFxOUqOcl1bBuJ6GnaR9D_a2dQ3WHcvqw3FhsmEYvghmcoYFysZpPirk3aneGjS6ztx56-AXRCgVdEtf32JdP3kTOe1QwifJQ_w4KK0MJCsR2z0gK-lTYWMa1zgs2PreTo8_mHAfTo=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-12T19:45:00.000Z", "utc_arrival": "2023-06-12T17:45:00.000Z", "local_departure": "2023-06-12T16:15:00.000Z", "utc_departure": "2023-06-12T14:15:00.000Z"}, {"id": "0b770a224c0c00005ba10d53_0|0a220b774c10000085c9a6d8_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 851.470304, "distance": 1975.87, "duration": {"departure": 12600, "return": 11400, "total": 24000}, "price": 266183.6796, "conversion": {"EUR": 696.804024, "HUF": 266183.6796}, "fare": {"adults": 133091.84, "children": 133091.84, "infants": 133091.84}, "bags_price": {"1": 102.774, "2": 205.548}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 4}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224c0c00005ba10d53_0", "combination_id": "0b770a224c0c00005ba10d53", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "FREG", "fare_category": "M", "fare_classes": "F", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-21T19:45:00.000Z", "utc_arrival": "2023-04-21T17:45:00.000Z", "local_departure": "2023-04-21T16:15:00.000Z", "utc_departure": "2023-04-21T14:15:00.000Z"}, {"id": "0a220b774c10000085c9a6d8_0", "combination_id": "0a220b774c10000085c9a6d8", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-25T14:05:00.000Z", "utc_arrival": "2023-04-25T12:05:00.000Z", "local_departure": "2023-04-25T10:55:00.000Z", "utc_departure": "2023-04-25T08:55:00.000Z"}], "booking_token": "EVvD-kUvml5KNLEprQC8nDxPwGkM23NZkl4Tbbf3WeT3wG2FWkkqKhM48g-mfIY2XR6ay7cY6IxDN5OxpnODsBrTvQOxiNW5FPGbtyrzG_uSM6HfzQk71px35tAmFhDs1il3H5i7hwg992cfn7MxljgdRzHL96hXvlQwx78JejPj7RyhIegZ0XLQ46gxSTSSTBVwh9tZEcPkErQ8CLPwuGAXJwHDKIRdhYKaCSqBlzshwgb3aF0MnR0j3tT4_mIBobNo93nX_Gw60l9Q5YHDrBFzcO7qatu17ra9AwIZCcLt8VLoeEEhhBaMKavG9z3SzBBe-mV4tBz72Ex02-HS6hbAXgVXpqjf3pyUzrfWF457MtR7B_YZsn2PFtSJgpGe5UWRIdlJPvAj3rN2Uoq4rTvx4sH9L5PlQ6YNBbw1alXsrzo-bJeXnBhN_hACqXrbQ1eQQj7FvgGwXHAZmmsJzcVEKD9GruHJQdEkZb_h3BiAhxtClNcyqfhFZ-kVnDI_SZTRpnU2zqBpuKqCuJ9Ox98PoLx4q2ezpwINfZ4zwn598lDynUFoXjC1NdmMGxk56r_3kDno4O3kHWU6tMfEFndtQXFgX2sDzc5OevcEEbUKSS2yzd2QDeB5_olLPROFduYw0Bcm9lfTE0NdHk3TNY8BE2TJCi9eElGRiXSBesCn22dmcdngghcL3ty_qXOhYIVxanyJrNPnAEUkbsxnr_hYQtSxFpp7pBkE5nO2YYHsbeKL0lToWg_KOnUL7y4LId4FO401DYqaLWwIev9ZZ6nX8YxrFiBy-qKOO54rJzv8=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c0c00005ba10d53_0%7C0a220b774c10000085c9a6d8_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EVvD-kUvml5KNLEprQC8nDxPwGkM23NZkl4Tbbf3WeT3wG2FWkkqKhM48g-mfIY2XR6ay7cY6IxDN5OxpnODsBrTvQOxiNW5FPGbtyrzG_uSM6HfzQk71px35tAmFhDs1il3H5i7hwg992cfn7MxljgdRzHL96hXvlQwx78JejPj7RyhIegZ0XLQ46gxSTSSTBVwh9tZEcPkErQ8CLPwuGAXJwHDKIRdhYKaCSqBlzshwgb3aF0MnR0j3tT4_mIBobNo93nX_Gw60l9Q5YHDrBFzcO7qatu17ra9AwIZCcLt8VLoeEEhhBaMKavG9z3SzBBe-mV4tBz72Ex02-HS6hbAXgVXpqjf3pyUzrfWF457MtR7B_YZsn2PFtSJgpGe5UWRIdlJPvAj3rN2Uoq4rTvx4sH9L5PlQ6YNBbw1alXsrzo-bJeXnBhN_hACqXrbQ1eQQj7FvgGwXHAZmmsJzcVEKD9GruHJQdEkZb_h3BiAhxtClNcyqfhFZ-kVnDI_SZTRpnU2zqBpuKqCuJ9Ox98PoLx4q2ezpwINfZ4zwn598lDynUFoXjC1NdmMGxk56r_3kDno4O3kHWU6tMfEFndtQXFgX2sDzc5OevcEEbUKSS2yzd2QDeB5_olLPROFduYw0Bcm9lfTE0NdHk3TNY8BE2TJCi9eElGRiXSBesCn22dmcdngghcL3ty_qXOhYIVxanyJrNPnAEUkbsxnr_hYQtSxFpp7pBkE5nO2YYHsbeKL0lToWg_KOnUL7y4LId4FO401DYqaLWwIev9ZZ6nX8YxrFiBy-qKOO54rJzv8=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-04-21T19:45:00.000Z", "utc_arrival": "2023-04-21T17:45:00.000Z", "local_departure": "2023-04-21T16:15:00.000Z", "utc_departure": "2023-04-21T14:15:00.000Z"}, {"id": "0b770a224c360000d7613bb9_0|0a220b774c390000563d5408_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 849.189776, "distance": 1975.87, "duration": {"departure": 11700, "return": 11700, "total": 23400}, "price": 266331.1846, "conversion": {"EUR": 697.190156, "HUF": 266331.1846}, "fare": {"adults": 133165.59, "children": 135736.36, "infants": 135736.36}, "bags_price": {"1": 97.09, "2": 203.98}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 158, "hold_height": 52, "hold_length": 78, "hold_weight": 20, "hold_width": 28, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 3, "personal_item_width": 15}, "availability": {"seats": 7}, "airlines": ["W6", "IB"], "route": [{"id": "0b770a224c360000d7613bb9_0", "combination_id": "0b770a224c360000d7613bb9", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "IB", "flight_no": 3279, "operating_carrier": "IB", "operating_flight_no": "3279", "fare_basis": "SZNNAOB4", "fare_category": "M", "fare_classes": "S", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-02T18:50:00.000Z", "utc_arrival": "2023-06-02T16:50:00.000Z", "local_departure": "2023-06-02T15:35:00.000Z", "utc_departure": "2023-06-02T13:35:00.000Z"}, {"id": "0a220b774c390000563d5408_0", "combination_id": "0a220b774c390000563d5408", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-05T23:45:00.000Z", "utc_arrival": "2023-06-05T21:45:00.000Z", "local_departure": "2023-06-05T20:30:00.000Z", "utc_departure": "2023-06-05T18:30:00.000Z"}], "booking_token": "EHY4CWYHszjQmODmEe-zl3Dfu4SPSxVILZbmmx_tYZ9Px-T-jax-eHPeaij4g6E6gvxr_xfIPh6c48RAsGQsEcnrWd1GknxSqVaTCv7O4t4DoLMgdeZkHpUbsvLTIVar7nVVty7OpFfIDNKfnVJOwIOUd-PAjz6cZRNMLYbNQyCZTwoe-9HBiJvl-T_CBoP0CFyv8A_hyLZfyz_XczRxbtliCRGBdLn7cEFMdXTuTGwyLddaWs5tksyFpdg9pxMX-P9_dblhxBxp97YJGde0-I_dVu2YdWbbbt-tisfxk1cSW9_iw5iEYDgAvsuWv_oG1dwaeSEjHcJMg9OCj9QnNWr6t0G2rqAcSH2oSbcaYU5hjYtLO8ejQBLTh2OqPYdAula5t0wUIni4LdoxnGXgZJzC-92RNkCbFNG8aG3Z__QHA_e1rl7B0SffctyajiBRzBViuXGpLwpcVfUdzypdZW-ytZSShhr4xbqD8yEmFT3TVDJUVZxuCWCrIrmw-22_SzfRB-smp8LN4p02QHkZ4m3JEwW0a8Rn4jFJFJfio8wXOCu7PV1-0a8dterzW_f2am90vTz4kcM6ucU8_Cj5hrXQYVlFuV5CTHTRSoHdOzcsQbIi3TkivoQ1cR_AU5GUVYPSTZqPBqFL5xAlC9ZmjVlx9dPUwQfxf-ukEGmDxkrVIAD4lhfFAyBQrX5Id1I0egU_A34UpiRaSEHtA63KGOlfiOmtXLPRgtMgCZlqEBB80Rcq3u297Dj__fYY6VYW0mCuMkTrVxYOmDPblVEJF_4aDfP5x_YnLqn89AMXOxjY=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c360000d7613bb9_0%7C0a220b774c390000563d5408_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EHY4CWYHszjQmODmEe-zl3Dfu4SPSxVILZbmmx_tYZ9Px-T-jax-eHPeaij4g6E6gvxr_xfIPh6c48RAsGQsEcnrWd1GknxSqVaTCv7O4t4DoLMgdeZkHpUbsvLTIVar7nVVty7OpFfIDNKfnVJOwIOUd-PAjz6cZRNMLYbNQyCZTwoe-9HBiJvl-T_CBoP0CFyv8A_hyLZfyz_XczRxbtliCRGBdLn7cEFMdXTuTGwyLddaWs5tksyFpdg9pxMX-P9_dblhxBxp97YJGde0-I_dVu2YdWbbbt-tisfxk1cSW9_iw5iEYDgAvsuWv_oG1dwaeSEjHcJMg9OCj9QnNWr6t0G2rqAcSH2oSbcaYU5hjYtLO8ejQBLTh2OqPYdAula5t0wUIni4LdoxnGXgZJzC-92RNkCbFNG8aG3Z__QHA_e1rl7B0SffctyajiBRzBViuXGpLwpcVfUdzypdZW-ytZSShhr4xbqD8yEmFT3TVDJUVZxuCWCrIrmw-22_SzfRB-smp8LN4p02QHkZ4m3JEwW0a8Rn4jFJFJfio8wXOCu7PV1-0a8dterzW_f2am90vTz4kcM6ucU8_Cj5hrXQYVlFuV5CTHTRSoHdOzcsQbIi3TkivoQ1cR_AU5GUVYPSTZqPBqFL5xAlC9ZmjVlx9dPUwQfxf-ukEGmDxkrVIAD4lhfFAyBQrX5Id1I0egU_A34UpiRaSEHtA63KGOlfiOmtXLPRgtMgCZlqEBB80Rcq3u297Dj__fYY6VYW0mCuMkTrVxYOmDPblVEJF_4aDfP5x_YnLqn89AMXOxjY=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-02T18:50:00.000Z", "utc_arrival": "2023-06-02T16:50:00.000Z", "local_departure": "2023-06-02T15:35:00.000Z", "utc_departure": "2023-06-02T13:35:00.000Z"}, {"id": "0b770a224c3500005ea303c4_0|0a220b774c390000563d5408_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 849.189776, "distance": 1975.87, "duration": {"departure": 11700, "return": 11700, "total": 23400}, "price": 266331.1846, "conversion": {"EUR": 697.190156, "HUF": 266331.1846}, "fare": {"adults": 133165.59, "children": 135736.36, "infants": 135736.36}, "bags_price": {"1": 97.09, "2": 203.98}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 158, "hold_height": 52, "hold_length": 78, "hold_weight": 20, "hold_width": 28, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 3, "personal_item_width": 15}, "availability": {"seats": 7}, "airlines": ["W6", "IB"], "route": [{"id": "0b770a224c3500005ea303c4_0", "combination_id": "0b770a224c3500005ea303c4", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "IB", "flight_no": 3279, "operating_carrier": "IB", "operating_flight_no": "3279", "fare_basis": "SZNNAOB4", "fare_category": "M", "fare_classes": "S", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-01T18:50:00.000Z", "utc_arrival": "2023-06-01T16:50:00.000Z", "local_departure": "2023-06-01T15:35:00.000Z", "utc_departure": "2023-06-01T13:35:00.000Z"}, {"id": "0a220b774c390000563d5408_0", "combination_id": "0a220b774c390000563d5408", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-05T23:45:00.000Z", "utc_arrival": "2023-06-05T21:45:00.000Z", "local_departure": "2023-06-05T20:30:00.000Z", "utc_departure": "2023-06-05T18:30:00.000Z"}], "booking_token": "EO5Hnh7t2VEDrkQiqDHYWCUwIpci7gMytZFkc7qo4hd0lQRpG39RYuHh8EtFhUCMMyiheM_s2M_0a_nqMevuIZqRCWKp1x6kHTtZwxhITA7KCFETaCsX2dEpYCl2iEOAV-sAEGeQVMXBITxftD0RWK87V4f8StvJemn2hZ3t1jFuo4zOMqv2WWYQvV7tI1aDB1pvISywkRLoHEM6JwQt0OUAUZtISUa5SHbD4dNn2nVEExnQ4noQ12_Fe03qKilBctZ0bc9kAsRPFzVKRJbp8OpInPACfGOUvnya0Vuo1RCFiLfbAP_dNw4z47rqiJx3ojQB0Aq4aP-Q9-J67Rc2kLPWVtFtjLgb6rXDP7bLekl7tmT4DRvy-fR4h2hq0htmneJXUC-xpevhAtsGmvsi5gDEqR9diGsPsPaqbTv50JDM6tR0yoj8gDvB493Z377evJPvN0r_gLT_p4_r4JVDsKxvNrisrNQzHn789ENMETicdNc-L4yzgwVQWieQa5h9fhJngcgn-9J6UeHqtd-m2zDDTY8d0Oev-TZAOEsM0vQkr1mF4L_Dx6U6zJIEcoT9NIafDZ1p3wJXKih42Q3uYc5X8odx49YSoPmTwM9IrAK3y-GAVmLDxQe6qNnBznsQe6N3y1G1N7zlrR1DI0PWCPRqkVD6KVKDRwG-RdWCh5hNDlhOxgNp0Y0_4FeZdn5TmFnXIt0EBm18KUtNuKkKgJ7ZgxRxZUd-XbTTchHMr91fNHl_W56EhqJqSe55VqkYGOS6cV4FO8WWu0VwD3omibgBueNMwZixz269yv8aOObg=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c3500005ea303c4_0%7C0a220b774c390000563d5408_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EO5Hnh7t2VEDrkQiqDHYWCUwIpci7gMytZFkc7qo4hd0lQRpG39RYuHh8EtFhUCMMyiheM_s2M_0a_nqMevuIZqRCWKp1x6kHTtZwxhITA7KCFETaCsX2dEpYCl2iEOAV-sAEGeQVMXBITxftD0RWK87V4f8StvJemn2hZ3t1jFuo4zOMqv2WWYQvV7tI1aDB1pvISywkRLoHEM6JwQt0OUAUZtISUa5SHbD4dNn2nVEExnQ4noQ12_Fe03qKilBctZ0bc9kAsRPFzVKRJbp8OpInPACfGOUvnya0Vuo1RCFiLfbAP_dNw4z47rqiJx3ojQB0Aq4aP-Q9-J67Rc2kLPWVtFtjLgb6rXDP7bLekl7tmT4DRvy-fR4h2hq0htmneJXUC-xpevhAtsGmvsi5gDEqR9diGsPsPaqbTv50JDM6tR0yoj8gDvB493Z377evJPvN0r_gLT_p4_r4JVDsKxvNrisrNQzHn789ENMETicdNc-L4yzgwVQWieQa5h9fhJngcgn-9J6UeHqtd-m2zDDTY8d0Oev-TZAOEsM0vQkr1mF4L_Dx6U6zJIEcoT9NIafDZ1p3wJXKih42Q3uYc5X8odx49YSoPmTwM9IrAK3y-GAVmLDxQe6qNnBznsQe6N3y1G1N7zlrR1DI0PWCPRqkVD6KVKDRwG-RdWCh5hNDlhOxgNp0Y0_4FeZdn5TmFnXIt0EBm18KUtNuKkKgJ7ZgxRxZUd-XbTTchHMr91fNHl_W56EhqJqSe55VqkYGOS6cV4FO8WWu0VwD3omibgBueNMwZixz269yv8aOObg=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-01T18:50:00.000Z", "utc_arrival": "2023-06-01T16:50:00.000Z", "local_departure": "2023-06-01T15:35:00.000Z", "utc_departure": "2023-06-01T13:35:00.000Z"}, {"id": "0b770a224c2e0000339b474d_0|0a220b774c3200001b9f20d5_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 856.602711, "distance": 1975.87, "duration": {"departure": 12600, "return": 11700, "total": 24300}, "price": 267634.9518, "conversion": {"EUR": 700.603101, "HUF": 267634.9518}, "fare": {"adults": 133817.48, "children": 139644.9, "infants": 139644.9}, "bags_price": {"1": 69.44, "2": 138.866}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 439, "hold_height": 149, "hold_length": 171, "hold_weight": 20, "hold_width": 119, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 7}, "airlines": ["W6"], "route": [{"id": "0b770a224c2e0000339b474d_0", "combination_id": "0b770a224c2e0000339b474d", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "HREG", "fare_category": "M", "fare_classes": "H", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-25T21:15:00.000Z", "utc_arrival": "2023-05-25T19:15:00.000Z", "local_departure": "2023-05-25T17:45:00.000Z", "utc_departure": "2023-05-25T15:45:00.000Z"}, {"id": "0a220b774c3200001b9f20d5_0", "combination_id": "0a220b774c3200001b9f20d5", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "GREG", "fare_category": "M", "fare_classes": "G", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-29T23:45:00.000Z", "utc_arrival": "2023-05-29T21:45:00.000Z", "local_departure": "2023-05-29T20:30:00.000Z", "utc_departure": "2023-05-29T18:30:00.000Z"}], "booking_token": "ElPBvRctGIAama9e0YdMJZU0VRTqkuuATMyD6qD-H8dF414zCMXURnO4dpsBjcjDi3M96Kr6naKNCQtz_eoHvg4taxpUuOpFolveX7usCRom07TxmjQ6evIU8UXTpnmLxVdf0neFZWGJ29Eg5Gk9H5GXvQDfI_wrGDEpDYKzvhbAPxdkCRvYtZ71H6q85w0yze7kWRDW1NMeGWVKIn_ccHBtwucoAQro12fnJrxjON_lFcHypUlKcqO0mOniqN_bG_WzbaOjgflfYoo4hjG5vrXwEWzI7UwIZK5SavABDE7emZmnw9web8Cg5V06azojJVOVImVhp5V7bN3ZT7UhyFOAVjKNvE1dwQLEjHKc266SDzoJKgTIXcptTAsFgFxE3h4Dv69SFutKBdZdgQsNUyJV9mHdI5044AmdlfI4Gc4XqrfRJljI4bo4jBgKkXcLAkXmxAB9JjSp85Bp2zM9Vu4W8GOHEgQ2KZuhGs0OEDVsa5U4GQ6Cwnrd1bi1WP7d_M34WGdIjUbhIXaWZoPrF--eirJ6SPcoXTn3BLHn5LmefK8SDh67z4VYEXqKeCqiV0eHEUt7F74kQWpI46fbbow_iKwloaMrfYBolYyXBmuMc15--h8aeCytLhK_d9xR9UvsYG35z7PoNHt9aUEz3UmnRMHZa_ZzgvKKwWiPWTdgXeA5ulYUaP8q3hCp5vckXM3NEp_vNFDVfHLrRl1hwCi_IkpTOKPCJ4vmaVV6GL_eSGClD7mwH8QpTCaIZ1MCxN_fMkoB2SlBkIS8IabIanWBlFbH6HVsAy2MqHQ2NcRM=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c2e0000339b474d_0%7C0a220b774c3200001b9f20d5_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=ElPBvRctGIAama9e0YdMJZU0VRTqkuuATMyD6qD-H8dF414zCMXURnO4dpsBjcjDi3M96Kr6naKNCQtz_eoHvg4taxpUuOpFolveX7usCRom07TxmjQ6evIU8UXTpnmLxVdf0neFZWGJ29Eg5Gk9H5GXvQDfI_wrGDEpDYKzvhbAPxdkCRvYtZ71H6q85w0yze7kWRDW1NMeGWVKIn_ccHBtwucoAQro12fnJrxjON_lFcHypUlKcqO0mOniqN_bG_WzbaOjgflfYoo4hjG5vrXwEWzI7UwIZK5SavABDE7emZmnw9web8Cg5V06azojJVOVImVhp5V7bN3ZT7UhyFOAVjKNvE1dwQLEjHKc266SDzoJKgTIXcptTAsFgFxE3h4Dv69SFutKBdZdgQsNUyJV9mHdI5044AmdlfI4Gc4XqrfRJljI4bo4jBgKkXcLAkXmxAB9JjSp85Bp2zM9Vu4W8GOHEgQ2KZuhGs0OEDVsa5U4GQ6Cwnrd1bi1WP7d_M34WGdIjUbhIXaWZoPrF--eirJ6SPcoXTn3BLHn5LmefK8SDh67z4VYEXqKeCqiV0eHEUt7F74kQWpI46fbbow_iKwloaMrfYBolYyXBmuMc15--h8aeCytLhK_d9xR9UvsYG35z7PoNHt9aUEz3UmnRMHZa_ZzgvKKwWiPWTdgXeA5ulYUaP8q3hCp5vckXM3NEp_vNFDVfHLrRl1hwCi_IkpTOKPCJ4vmaVV6GL_eSGClD7mwH8QpTCaIZ1MCxN_fMkoB2SlBkIS8IabIanWBlFbH6HVsAy2MqHQ2NcRM=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-25T21:15:00.000Z", "utc_arrival": "2023-05-25T19:15:00.000Z", "local_departure": "2023-05-25T17:45:00.000Z", "utc_departure": "2023-05-25T15:45:00.000Z"}, {"id": "0b770a224c0f0000d159abac_0|0a220b774c1200004e293ac3_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 855.291121, "distance": 1975.87, "duration": {"departure": 12000, "return": 11700, "total": 23700}, "price": 268152.5974, "conversion": {"EUR": 701.958171, "HUF": 268152.5974}, "fare": {"adults": 134076.3, "children": 134076.3, "infants": 134076.3}, "bags_price": {"1": 84.448, "2": 168.896}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 3}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224c0f0000d159abac_0", "combination_id": "0b770a224c0f0000d159abac", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-24T14:00:00.000Z", "utc_arrival": "2023-04-24T12:00:00.000Z", "local_departure": "2023-04-24T10:40:00.000Z", "utc_departure": "2023-04-24T08:40:00.000Z"}, {"id": "0a220b774c1200004e293ac3_0", "combination_id": "0a220b774c1200004e293ac3", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "GFREG", "fare_category": "M", "fare_classes": "G", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-28T01:15:00.000Z", "utc_arrival": "2023-04-27T23:15:00.000Z", "local_departure": "2023-04-27T22:00:00.000Z", "utc_departure": "2023-04-27T20:00:00.000Z"}], "booking_token": "EAlmIlPDr6Lyr9DtFMmzpKpF5MYwHFvRvnau6yaJEbC6V_SS0iLBD6e5tA_yacwBvosvMZ6E_26ZhimW6q7J6trk8BbKRBNh15HMrXidBqtB5Iq5Y6oUHw3njuUBizqBepCVfJYEnDLtAGNZ9d66ziuuO9slTSn57rPQ2dB2uCC8584OYxLWSZXy-cVmsbvW_Jd1xN-ug4RxfQv14v46Fx4W1G2hrPdJJDS-HL6prE5wE9o4WX2NipKaTPQTwKb_CW143c261xIXmz4_FZfVIl7I8S3iet-6ZaHXpsWVDgiKPXNtbUm6Vo_ibFfPU-WblMUbcEGK_yx5C7pyD6FeU1cKou82nCx5jdgvRRP3Fd1BD-K7wFf84PIMysj_BsOzAxor45Kfs47fgtHYtxYFvTxwYink8R_DoLAltkcJUTcVlSPUVbBi3W-GYpCyMhlTKvA1T3Mkh3lkq0amzD9rLN2KAm_Fjnbu5Mxax56Hr_daeWVm_ajzptaiGpXwPsRi67q-ozIKC_eCezw-UK7IoX-i3yBgFn9wJL2tcXautKyaotjbdL-5WrL8yBNoZVjDf4Ro9axBt88mJpZQp9Q1MO42wzTNiectk56Vg4twgRO4h5jCb0BJtYYFEXlPUmYriILm-UgZszHfdVEngHRrg3VIivW3r9Uu73BNoPm22uDhn740Iw2ZAu2nAXCdC83b-ADKjIKgK-4YcRWcLQf_yxcpjE8CQAdNzt1K1ERzEmC-2wO6zmDQQWuMeSazICrn0NghRCg0gkLwgY15xjAQCD8XWNOxwyJLInki9cln17-k=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c0f0000d159abac_0%7C0a220b774c1200004e293ac3_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EAlmIlPDr6Lyr9DtFMmzpKpF5MYwHFvRvnau6yaJEbC6V_SS0iLBD6e5tA_yacwBvosvMZ6E_26ZhimW6q7J6trk8BbKRBNh15HMrXidBqtB5Iq5Y6oUHw3njuUBizqBepCVfJYEnDLtAGNZ9d66ziuuO9slTSn57rPQ2dB2uCC8584OYxLWSZXy-cVmsbvW_Jd1xN-ug4RxfQv14v46Fx4W1G2hrPdJJDS-HL6prE5wE9o4WX2NipKaTPQTwKb_CW143c261xIXmz4_FZfVIl7I8S3iet-6ZaHXpsWVDgiKPXNtbUm6Vo_ibFfPU-WblMUbcEGK_yx5C7pyD6FeU1cKou82nCx5jdgvRRP3Fd1BD-K7wFf84PIMysj_BsOzAxor45Kfs47fgtHYtxYFvTxwYink8R_DoLAltkcJUTcVlSPUVbBi3W-GYpCyMhlTKvA1T3Mkh3lkq0amzD9rLN2KAm_Fjnbu5Mxax56Hr_daeWVm_ajzptaiGpXwPsRi67q-ozIKC_eCezw-UK7IoX-i3yBgFn9wJL2tcXautKyaotjbdL-5WrL8yBNoZVjDf4Ro9axBt88mJpZQp9Q1MO42wzTNiectk56Vg4twgRO4h5jCb0BJtYYFEXlPUmYriILm-UgZszHfdVEngHRrg3VIivW3r9Uu73BNoPm22uDhn740Iw2ZAu2nAXCdC83b-ADKjIKgK-4YcRWcLQf_yxcpjE8CQAdNzt1K1ERzEmC-2wO6zmDQQWuMeSazICrn0NghRCg0gkLwgY15xjAQCD8XWNOxwyJLInki9cln17-k=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-04-24T14:00:00.000Z", "utc_arrival": "2023-04-24T12:00:00.000Z", "local_departure": "2023-04-24T10:40:00.000Z", "utc_departure": "2023-04-24T08:40:00.000Z"}, {"id": "0b770a224c2b00007aa0884e_0|0a220b774c2f00005a82fb6a_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 862.831862, "distance": 1975.87, "duration": {"departure": 12000, "return": 12900, "total": 24900}, "price": 268995.8466, "conversion": {"EUR": 704.165592, "HUF": 268995.8466}, "fare": {"adults": 134497.92, "children": 134497.92, "infants": 134497.92}, "bags_price": {"1": 69.314, "2": 138.628}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 5}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224c2b00007aa0884e_0", "combination_id": "0b770a224c2b00007aa0884e", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-22T14:00:00.000Z", "utc_arrival": "2023-05-22T12:00:00.000Z", "local_departure": "2023-05-22T10:40:00.000Z", "utc_departure": "2023-05-22T08:40:00.000Z"}, {"id": "0a220b774c2f00005a82fb6a_0", "combination_id": "0a220b774c2f00005a82fb6a", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "FREG", "fare_category": "M", "fare_classes": "F", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-27T00:05:00.000Z", "utc_arrival": "2023-05-26T22:05:00.000Z", "local_departure": "2023-05-26T20:30:00.000Z", "utc_departure": "2023-05-26T18:30:00.000Z"}], "booking_token": "ESQqlNfLKUrCn9FgB8udWZDwaxcdODRB6A36SmD85gAJHlOXi9KY4eMFk5UkWC8SmnqvTYw24uLoXBHn_AHdjvz4F9z6Xy2IoYwTPr3bwk5UsMey55tKdZGBQdDgVgtnei8SujinZQNgC53wAEeJhwZqBv-JJFlqwIE0X45Fs3sbj-uIjDVjcFfDXABrERVnTAafnBcVS0rxKgMEptzmMYh18S84sxEIEiEGiJGcoHOKPHyfebo3SHRwLUcPi9_8qJnV5JXarYu6OcvjpCzCZxjayQR5gjccchUZ8ip8152K4IoAr8N1dOID1-grmKpyIylj9FLbh-3rz5MhRX9ozKQw1gGnuB3lsMXg6CLgs3jN2g0ilIwAFHMROG77mF_XctKg2lvxrwDyQWLczXbhdAf9o1dhSd8G4ZVOaYveO46MSkkwLQP7m5RIpbYc1YgUkX6DF5ZnyIN8h91O6fOnY3DlTD8eGgK-eoaTt4VVfL_mDfkppPG-3QwsMwMg9sIoyqrOtFYiD_5tI_wu5es0jgKdA9XqJg01DAlzKcsfzlNN5fS7I0yfm36uBXY9JJZmnyJE3umRIGWg-a_JV3zaSFjcxiu4a3lVKnsm4JdCNv3M6vHZyfxkzydMfv8Jfs0Cjo5NLNYYhbvTqWQkdmokKCZcLWDIX1_GRJ4wLwViuGJbD0RtXDj8AWmCLfkilPnBvPz3vR5d5ErZ8blxOxTBKBzynz6IqUIcfr8XqjbX_CODUEPMYsNnOLFaaQDtjYUXH9a5P0qCcDsks7W7z-hHaFfERhQ7Tc-hmalS8YET048M=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c2b00007aa0884e_0%7C0a220b774c2f00005a82fb6a_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=ESQqlNfLKUrCn9FgB8udWZDwaxcdODRB6A36SmD85gAJHlOXi9KY4eMFk5UkWC8SmnqvTYw24uLoXBHn_AHdjvz4F9z6Xy2IoYwTPr3bwk5UsMey55tKdZGBQdDgVgtnei8SujinZQNgC53wAEeJhwZqBv-JJFlqwIE0X45Fs3sbj-uIjDVjcFfDXABrERVnTAafnBcVS0rxKgMEptzmMYh18S84sxEIEiEGiJGcoHOKPHyfebo3SHRwLUcPi9_8qJnV5JXarYu6OcvjpCzCZxjayQR5gjccchUZ8ip8152K4IoAr8N1dOID1-grmKpyIylj9FLbh-3rz5MhRX9ozKQw1gGnuB3lsMXg6CLgs3jN2g0ilIwAFHMROG77mF_XctKg2lvxrwDyQWLczXbhdAf9o1dhSd8G4ZVOaYveO46MSkkwLQP7m5RIpbYc1YgUkX6DF5ZnyIN8h91O6fOnY3DlTD8eGgK-eoaTt4VVfL_mDfkppPG-3QwsMwMg9sIoyqrOtFYiD_5tI_wu5es0jgKdA9XqJg01DAlzKcsfzlNN5fS7I0yfm36uBXY9JJZmnyJE3umRIGWg-a_JV3zaSFjcxiu4a3lVKnsm4JdCNv3M6vHZyfxkzydMfv8Jfs0Cjo5NLNYYhbvTqWQkdmokKCZcLWDIX1_GRJ4wLwViuGJbD0RtXDj8AWmCLfkilPnBvPz3vR5d5ErZ8blxOxTBKBzynz6IqUIcfr8XqjbX_CODUEPMYsNnOLFaaQDtjYUXH9a5P0qCcDsks7W7z-hHaFfERhQ7Tc-hmalS8YET048M=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-22T14:00:00.000Z", "utc_arrival": "2023-05-22T12:00:00.000Z", "local_departure": "2023-05-22T10:40:00.000Z", "utc_departure": "2023-05-22T08:40:00.000Z"}, {"id": "0b770a224c16000004d61df8_0|0a220b774c190000a5259c8e_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 860.558442, "distance": 1975.87, "duration": {"departure": 12000, "return": 11700, "total": 23700}, "price": 270164.7483, "conversion": {"EUR": 707.225492, "HUF": 270164.7483}, "fare": {"adults": 135082.37, "children": 135082.37, "infants": 135082.37}, "bags_price": {"1": 90.552, "2": 166.852}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 6}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224c16000004d61df8_0", "combination_id": "0b770a224c16000004d61df8", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-01T14:00:00.000Z", "utc_arrival": "2023-05-01T12:00:00.000Z", "local_departure": "2023-05-01T10:40:00.000Z", "utc_departure": "2023-05-01T08:40:00.000Z"}, {"id": "0a220b774c190000a5259c8e_0", "combination_id": "0a220b774c190000a5259c8e", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IJREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-05T01:15:00.000Z", "utc_arrival": "2023-05-04T23:15:00.000Z", "local_departure": "2023-05-04T22:00:00.000Z", "utc_departure": "2023-05-04T20:00:00.000Z"}], "booking_token": "EzwkpPTwoTvx3-TvEK6MXccWixdil7lWekTPta1Hd70MGcHI_axxK7X5QTF4D06qF6DXmdOjLet6ImYnwYkE7Hd-rDkOfrl70xeAMIbGs9uErB6LmjFf6clShB4ZdBgVwpAv_DroZ3hN45m2t5rz1vuxmjEu3gxuUJvFw-JbF1a68dl6ySgHwl8nTJQ8I5kz0dLrSnJ21hcTlFwcsQIqA7tKhE3_PkWijaSOdclmo6Ueapn64oxhJVKuItsvk3VZhI89D6D8kN0Rsl_gd_FSVd_xovyL4sTPLhBEDecS0-v5cgxkf6kQlgj2-E4VxRHlAyOTGZJw_asQIHot6HJpM2vnIGfxwKMqf1-3Pi_qtnqqv-XFEtnK5tVKVfbvb7e73NbZBaERHaHVMfDTQlq_v0cvMtidNt-37lMEGBKrmzDehW7ZhtKyi6xOMji6kSpD6NXV2N0hrPuW1w0muW9g3YphSYOTe2XiOFtyARPi8L6REVo6cjo5W6ebzNLvfcHnYwmmpwDWRlLo4KB3V6UPvtTMN_zkfQu5uo-zR11fYA7P3dPeMu_2g8SyWb8uK4DS1QqRKJF_ls1WMxPPBhOdah2JvZx8Ap4N8JEfL1iMnp5uuYAAwLhdMPXmCeBI5ysueh-pAdwEnu0ds0PjWSckP_CtbhHpJBHZ3aEzSHpkg06zie6ilkDBfGG6LQH5PbdP_uqeN10Kq13nkYID2xdVtvh6LyHV0y6-qFjgC_6B3llMbs3oPr3lFZIUl-6t3UPiiok5auY4x-VGc1i3cm3utvFLZ45kJJNvUUhQDG6eOmpk=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c16000004d61df8_0%7C0a220b774c190000a5259c8e_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EzwkpPTwoTvx3-TvEK6MXccWixdil7lWekTPta1Hd70MGcHI_axxK7X5QTF4D06qF6DXmdOjLet6ImYnwYkE7Hd-rDkOfrl70xeAMIbGs9uErB6LmjFf6clShB4ZdBgVwpAv_DroZ3hN45m2t5rz1vuxmjEu3gxuUJvFw-JbF1a68dl6ySgHwl8nTJQ8I5kz0dLrSnJ21hcTlFwcsQIqA7tKhE3_PkWijaSOdclmo6Ueapn64oxhJVKuItsvk3VZhI89D6D8kN0Rsl_gd_FSVd_xovyL4sTPLhBEDecS0-v5cgxkf6kQlgj2-E4VxRHlAyOTGZJw_asQIHot6HJpM2vnIGfxwKMqf1-3Pi_qtnqqv-XFEtnK5tVKVfbvb7e73NbZBaERHaHVMfDTQlq_v0cvMtidNt-37lMEGBKrmzDehW7ZhtKyi6xOMji6kSpD6NXV2N0hrPuW1w0muW9g3YphSYOTe2XiOFtyARPi8L6REVo6cjo5W6ebzNLvfcHnYwmmpwDWRlLo4KB3V6UPvtTMN_zkfQu5uo-zR11fYA7P3dPeMu_2g8SyWb8uK4DS1QqRKJF_ls1WMxPPBhOdah2JvZx8Ap4N8JEfL1iMnp5uuYAAwLhdMPXmCeBI5ysueh-pAdwEnu0ds0PjWSckP_CtbhHpJBHZ3aEzSHpkg06zie6ilkDBfGG6LQH5PbdP_uqeN10Kq13nkYID2xdVtvh6LyHV0y6-qFjgC_6B3llMbs3oPr3lFZIUl-6t3UPiiok5auY4x-VGc1i3cm3utvFLZ45kJJNvUUhQDG6eOmpk=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-01T14:00:00.000Z", "utc_arrival": "2023-05-01T12:00:00.000Z", "local_departure": "2023-05-01T10:40:00.000Z", "utc_departure": "2023-05-01T08:40:00.000Z"}, {"id": "0b770a224bfa0000e3b3cbb8_0|0a220b774bfd0000e604e9be_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 860.820823, "distance": 1975.87, "duration": {"departure": 12000, "return": 11700, "total": 23700}, "price": 270264.9796, "conversion": {"EUR": 707.487873, "HUF": 270264.9796}, "fare": {"adults": 135132.49, "children": 135132.49, "infants": 135132.49}, "bags_price": {"1": 110.404, "2": 193.704}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 3}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224bfa0000e3b3cbb8_0", "combination_id": "0b770a224bfa0000e3b3cbb8", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-03T14:00:00.000Z", "utc_arrival": "2023-04-03T12:00:00.000Z", "local_departure": "2023-04-03T10:40:00.000Z", "utc_departure": "2023-04-03T08:40:00.000Z"}, {"id": "0a220b774bfd0000e604e9be_0", "combination_id": "0a220b774bfd0000e604e9be", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-07T01:15:00.000Z", "utc_arrival": "2023-04-06T23:15:00.000Z", "local_departure": "2023-04-06T22:00:00.000Z", "utc_departure": "2023-04-06T20:00:00.000Z"}], "booking_token": "E1c03UOhe5cnA2i5-f-Av-gjp7BLzPAIWwAZLGwGIrx2jKyeiFgpCzw-Rhy3rf3IfG6nwxUR2XlrI5-cnGWNK_QDry4v6nss9WWXOp3TaXF6lVc4lKi9LoSqPi4JfU6SOu34o-TyTSCui2pwQTQLeClavQxCG2_HSdZtU4dvWigxTNM2A7lNicWoFuekRyXzLMpa5NOR3rRKnEM_SFzxQg6EN0g1YcoDk05CWXiGUhY3yI00Z50KyxGifaxTWJzpvGy3AkCp5gP9CKq-bD-r9L2ugBGRAv_D3OfMXFSA9iE8SOVCXfekkm0jByNWVsfqxUelYQ8Ko9k-o6V_GmzjMLus1FLuPbLaygnsVLzFj6h30KGbGqxaC_EKR9voMqRVV_YVP_gm-gwUMvUjNhqwtXboc9azU4fozb9DrbByyQbDEUYnvW37Ycg6mukjjhCjnvSgBq6oCP7OVvtOpkHIBngSAjWo5YzLMKsOsF2MRwP3fDpQpQVagt_SieIXNOnaodb_YNkLDwAKN_fa-N1roaHdawNp_g57XL-0ELsAnBxxQALKY4Wu2EIAZURO_2U4aoADtaKTE3n3jeoVZ9HL5hLgKqIUS4P4cJAlu7uj53dEmfa9rjdoMYUsqnSP3Vd55MHgYcwBYM-Xb7skiG53eWUw8V8xqpOowmy89pW2Vo3iHcF6n3ZXW_Wj92kHMF_eW_S_8JHVumaZG78Jf6Y0LWGAjMQjvdPx6zMqBaXDgTe31AcCmv_eiR1N-3gzMf4w2clbQTYTr4gO27pZFyfgrRw==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224bfa0000e3b3cbb8_0%7C0a220b774bfd0000e604e9be_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=E1c03UOhe5cnA2i5-f-Av-gjp7BLzPAIWwAZLGwGIrx2jKyeiFgpCzw-Rhy3rf3IfG6nwxUR2XlrI5-cnGWNK_QDry4v6nss9WWXOp3TaXF6lVc4lKi9LoSqPi4JfU6SOu34o-TyTSCui2pwQTQLeClavQxCG2_HSdZtU4dvWigxTNM2A7lNicWoFuekRyXzLMpa5NOR3rRKnEM_SFzxQg6EN0g1YcoDk05CWXiGUhY3yI00Z50KyxGifaxTWJzpvGy3AkCp5gP9CKq-bD-r9L2ugBGRAv_D3OfMXFSA9iE8SOVCXfekkm0jByNWVsfqxUelYQ8Ko9k-o6V_GmzjMLus1FLuPbLaygnsVLzFj6h30KGbGqxaC_EKR9voMqRVV_YVP_gm-gwUMvUjNhqwtXboc9azU4fozb9DrbByyQbDEUYnvW37Ycg6mukjjhCjnvSgBq6oCP7OVvtOpkHIBngSAjWo5YzLMKsOsF2MRwP3fDpQpQVagt_SieIXNOnaodb_YNkLDwAKN_fa-N1roaHdawNp_g57XL-0ELsAnBxxQALKY4Wu2EIAZURO_2U4aoADtaKTE3n3jeoVZ9HL5hLgKqIUS4P4cJAlu7uj53dEmfa9rjdoMYUsqnSP3Vd55MHgYcwBYM-Xb7skiG53eWUw8V8xqpOowmy89pW2Vo3iHcF6n3ZXW_Wj92kHMF_eW_S_8JHVumaZG78Jf6Y0LWGAjMQjvdPx6zMqBaXDgTe31AcCmv_eiR1N-3gzMf4w2clbQTYTr4gO27pZFyfgrRw==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-04-03T14:00:00.000Z", "utc_arrival": "2023-04-03T12:00:00.000Z", "local_departure": "2023-04-03T10:40:00.000Z", "utc_departure": "2023-04-03T08:40:00.000Z"}, {"id": "0b770a224bf000009aab5dae_0|0a220b774bf400002dbcb9a5_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 860.002508, "distance": 1975.87, "duration": {"departure": 12000, "return": 11400, "total": 23400}, "price": 270461.7187, "conversion": {"EUR": 708.002888, "HUF": 270461.7187}, "fare": {"adults": 135230.86, "children": 138232.33, "infants": 138232.33}, "bags_price": {"1": 97.104, "2": 194.222}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 6}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224bf000009aab5dae_0", "combination_id": "0b770a224bf000009aab5dae", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "HREG", "fare_category": "M", "fare_classes": "H", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-03-24T19:40:00.000Z", "utc_arrival": "2023-03-24T18:40:00.000Z", "local_departure": "2023-03-24T16:20:00.000Z", "utc_departure": "2023-03-24T15:20:00.000Z"}, {"id": "0a220b774bf400002dbcb9a5_0", "combination_id": "0a220b774bf400002dbcb9a5", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-03-28T14:05:00.000Z", "utc_arrival": "2023-03-28T12:05:00.000Z", "local_departure": "2023-03-28T10:55:00.000Z", "utc_departure": "2023-03-28T08:55:00.000Z"}], "booking_token": "E8WiqWaIlq3xXIRsUSv6q1ct4Mzt5_Dqvdwv5fIYwsDhhwUexHO8bRruBPziV5Ms7RRTAGemH1fr8DrdI4qpVlm_9hTLEoOqQF7OPlJBMD4zS2pRWO1Mf9xb8VIiNRydL0xod99VwCS6YAFZIjiHHeQi0ITcoOXXfPFWWRBqMdXVhRKVmmyQPUP5ki7DSqfAyDij8D-1nY7tYWD1HOqZx_wRpDs3snLoyszwa6ATO4vP77hkm9ROb4xFNoJZ402RaH71lyxpW85jwHMYXZUzkKXb447CMbntNXaCKgEpJn4sWcyUTXrKnzkkXXApCHJInCFLvQNDwzxkwQHv5xYth7kRJEzjZmuJDxk1SSTkX-REgMfh3PyEgqp0e-R94DuXRoJhDE-GfAvqEs4v1yKmh9N4jl97qxk9BxTi6-14veayKFji2SUiejLYVFEPzTTb9p1knpuo0u7LLmAJer5A56RaBs1Q0geOXGyTsY4NftBralG1D15cQPMseDM4YRcsh7FJlyLek93rv-DsEBiSci15REV0smPFl2fZy0LKqm7_ASvkOaStcJ4Wkt9xiVQZkZ2Oq9xt8DxgSbvz1lrfr_u0w5V83l-MaJQOY4bLPnhrCW5rK2ljkVvJ0Xe_SwUY53H4MznbDx15OUyH6yqW4cgHQt62jGsyuEO_uW5_j6_WgPKARhVOd3FA5ERNKl0ZzePFFqWpQwbXGzl_8n2-dQjMbqO9IaIvFou05HPppLBtLFQL-YqbQhMGzpRybsYX0TBm1-q1AkbWF-AxTIvg2bjUN8lH7heOsXHvHA6xc9FU=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224bf000009aab5dae_0%7C0a220b774bf400002dbcb9a5_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=E8WiqWaIlq3xXIRsUSv6q1ct4Mzt5_Dqvdwv5fIYwsDhhwUexHO8bRruBPziV5Ms7RRTAGemH1fr8DrdI4qpVlm_9hTLEoOqQF7OPlJBMD4zS2pRWO1Mf9xb8VIiNRydL0xod99VwCS6YAFZIjiHHeQi0ITcoOXXfPFWWRBqMdXVhRKVmmyQPUP5ki7DSqfAyDij8D-1nY7tYWD1HOqZx_wRpDs3snLoyszwa6ATO4vP77hkm9ROb4xFNoJZ402RaH71lyxpW85jwHMYXZUzkKXb447CMbntNXaCKgEpJn4sWcyUTXrKnzkkXXApCHJInCFLvQNDwzxkwQHv5xYth7kRJEzjZmuJDxk1SSTkX-REgMfh3PyEgqp0e-R94DuXRoJhDE-GfAvqEs4v1yKmh9N4jl97qxk9BxTi6-14veayKFji2SUiejLYVFEPzTTb9p1knpuo0u7LLmAJer5A56RaBs1Q0geOXGyTsY4NftBralG1D15cQPMseDM4YRcsh7FJlyLek93rv-DsEBiSci15REV0smPFl2fZy0LKqm7_ASvkOaStcJ4Wkt9xiVQZkZ2Oq9xt8DxgSbvz1lrfr_u0w5V83l-MaJQOY4bLPnhrCW5rK2ljkVvJ0Xe_SwUY53H4MznbDx15OUyH6yqW4cgHQt62jGsyuEO_uW5_j6_WgPKARhVOd3FA5ERNKl0ZzePFFqWpQwbXGzl_8n2-dQjMbqO9IaIvFou05HPppLBtLFQL-YqbQhMGzpRybsYX0TBm1-q1AkbWF-AxTIvg2bjUN8lH7heOsXHvHA6xc9FU=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-03-24T19:40:00.000Z", "utc_arrival": "2023-03-24T18:40:00.000Z", "local_departure": "2023-03-24T16:20:00.000Z", "utc_departure": "2023-03-24T15:20:00.000Z"}, {"id": "0b770a224c240000ea08a5dc_0|0a220b774c270000e6ac7939_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 862.734002, "distance": 1975.87, "duration": {"departure": 12000, "return": 11700, "total": 23700}, "price": 270995.8264, "conversion": {"EUR": 709.401052, "HUF": 270995.8264}, "fare": {"adults": 135497.91, "children": 135497.91, "infants": 135497.91}, "bags_price": {"1": 79.702, "2": 159.418}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 2}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224c240000ea08a5dc_0", "combination_id": "0b770a224c240000ea08a5dc", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-15T14:00:00.000Z", "utc_arrival": "2023-05-15T12:00:00.000Z", "local_departure": "2023-05-15T10:40:00.000Z", "utc_departure": "2023-05-15T08:40:00.000Z"}, {"id": "0a220b774c270000e6ac7939_0", "combination_id": "0a220b774c270000e6ac7939", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "HIREG", "fare_category": "M", "fare_classes": "H", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-19T01:15:00.000Z", "utc_arrival": "2023-05-18T23:15:00.000Z", "local_departure": "2023-05-18T22:00:00.000Z", "utc_departure": "2023-05-18T20:00:00.000Z"}], "booking_token": "EtXjpjMCzKyaeWd0bA0dh4Z-9PDatWVohTVi6Agj12uw7N5UG329HSPySQwGpJVOEEZzrUOlHAs8lS8W-rIjQMDlKZEfcCdkq-NgJ2q7GqiFQZNgseApLyRVg4Mff6YdxU-SQrtcrS7tra0WqpNylORoH9BIHt0W22danapNEQYKs7LvTItseBuc-MjgcVBLV4ZPL-CMdTyvlE2ZsrmJIJTU7cI-8B4lpeoLYiUIzBMGEXV5mABsCUHMz02mWLTZ60pj387zR2Qo7Z-p_2uTzcjkONn7XRHQ0_OOaQbbrxg7LDxOJqsDCjts8k5DLZp1VP-hloQrJLULSx4_1f_60pU-lIOlVeq6mwwQQ6Spmoesm568tnTVPCP1AIAmcoZixb6wYfXsda0DQe94Tps04vUsdghxwHfsG_wcqg909Aa7a6m-npgS8ZqixJOWBbgHPjrYyBrtutWUKwTLkdOATkIxAKXbuFrR1_cuv_akXGx7zkKwQCZz9Cm57xe8CmSPfD-dH_oL-QgEFISGvSsATFWbCb_9_CcG8_U0s5xESoV-3_1Sy9Kz-rQqk-j6bH6K45t6RPSQQtDBm_XFWqObor_YbAxU15NPp9sV-ZZUDke1CySv7KwiGjqMw1mHcpANWvZKGw8zYAiw88-rO5ctUZyfeEw1tpMrE8tZd9EJr4wak4yriWyafC6dQxXhLYMJAyNZiXXZLr97-SlPWwSRwRQgGuVOdsXqbdXZFtMICkIQ49tzhpP6-iKcE-dzIhh5w0jUTB7p5EmCpM_nDWHSJygUriG6keVd7XeWIGJv4FBE=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c240000ea08a5dc_0%7C0a220b774c270000e6ac7939_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EtXjpjMCzKyaeWd0bA0dh4Z-9PDatWVohTVi6Agj12uw7N5UG329HSPySQwGpJVOEEZzrUOlHAs8lS8W-rIjQMDlKZEfcCdkq-NgJ2q7GqiFQZNgseApLyRVg4Mff6YdxU-SQrtcrS7tra0WqpNylORoH9BIHt0W22danapNEQYKs7LvTItseBuc-MjgcVBLV4ZPL-CMdTyvlE2ZsrmJIJTU7cI-8B4lpeoLYiUIzBMGEXV5mABsCUHMz02mWLTZ60pj387zR2Qo7Z-p_2uTzcjkONn7XRHQ0_OOaQbbrxg7LDxOJqsDCjts8k5DLZp1VP-hloQrJLULSx4_1f_60pU-lIOlVeq6mwwQQ6Spmoesm568tnTVPCP1AIAmcoZixb6wYfXsda0DQe94Tps04vUsdghxwHfsG_wcqg909Aa7a6m-npgS8ZqixJOWBbgHPjrYyBrtutWUKwTLkdOATkIxAKXbuFrR1_cuv_akXGx7zkKwQCZz9Cm57xe8CmSPfD-dH_oL-QgEFISGvSsATFWbCb_9_CcG8_U0s5xESoV-3_1Sy9Kz-rQqk-j6bH6K45t6RPSQQtDBm_XFWqObor_YbAxU15NPp9sV-ZZUDke1CySv7KwiGjqMw1mHcpANWvZKGw8zYAiw88-rO5ctUZyfeEw1tpMrE8tZd9EJr4wak4yriWyafC6dQxXhLYMJAyNZiXXZLr97-SlPWwSRwRQgGuVOdsXqbdXZFtMICkIQ49tzhpP6-iKcE-dzIhh5w0jUTB7p5EmCpM_nDWHSJygUriG6keVd7XeWIGJv4FBE=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-15T14:00:00.000Z", "utc_arrival": "2023-05-15T12:00:00.000Z", "local_departure": "2023-05-15T10:40:00.000Z", "utc_departure": "2023-05-15T08:40:00.000Z"}, {"id": "0b770a224c130000597a9e5b_0|0a220b774c170000387ba921_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 874.872564, "distance": 1975.87, "duration": {"departure": 12600, "return": 11400, "total": 24000}, "price": 275123.4955, "conversion": {"EUR": 720.206284, "HUF": 275123.4955}, "fare": {"adults": 137561.75, "children": 137561.75, "infants": 137561.75}, "bags_price": {"1": 108.962, "2": 215.152}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 5}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224c130000597a9e5b_0", "combination_id": "0b770a224c130000597a9e5b", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "KREG", "fare_category": "M", "fare_classes": "K", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-28T19:45:00.000Z", "utc_arrival": "2023-04-28T17:45:00.000Z", "local_departure": "2023-04-28T16:15:00.000Z", "utc_departure": "2023-04-28T14:15:00.000Z"}, {"id": "0a220b774c170000387ba921_0", "combination_id": "0a220b774c170000387ba921", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-02T14:05:00.000Z", "utc_arrival": "2023-05-02T12:05:00.000Z", "local_departure": "2023-05-02T10:55:00.000Z", "utc_departure": "2023-05-02T08:55:00.000Z"}], "booking_token": "EQ8hU5rHthQDU2n1TYDLOmlpxsiKoF6JqGL4WFV-WeoJNcqOLXZZKpabkgoeSQlady_Y7pLMrQGdGyESO7pAjdZIlg_JEWmLtvt77V2J8iIm1_Bqve-a2_xbTDxxKcUeNnYp5x7SwPN4Pp86gihXC96vMeFbvMg5KPHVZDeKIKdNexEl_wPkSVMQDcZbHVhMGtcZm6z9b058JlspYs_Re7-vVgCPw1UuaEpJiibajOrFDHeGZsa18hEOhzzaXg5BY6XGvVO3fletuQG6rErZtrVSTn1h5zdH0uChYM2I7PFygRKVESCd_ZEV563th6gIvcrPpwRC_gldwtJjHMuQN0ee8RfbktLC1or5n0iHDmVGXjfwNT7WYlU4fxGrxvToqzdxTZ1pbTS0C96C3LAXonZ0pqQCeu1CeqYBXNAHfY6FhEbm85xlSaE8tutNdvmYBjiNsSBA5PrZU0DQ00l9w8qky1OC80AO8QTeQu17rXJP001_uugfyfyipz307w_-bBOBH4osNsw4LOc_lPjzZquiyzo8iCLZbLpVIP9bXkCEUEx5AwtIEE8IBimhX0K0MxhOQhZ-ZSSYmD5FJir-0X233Lbmw3CtHD8yGzUY9hN14XrXD0bQJgUh68kMFOT2lBauf9Gov23RdMehZ34kcl6uDMna02eL5KcQcH-z84DNEPvd7TNFc816Dd_uzc_AWW6Ey3Of7bTTGcPXfgVqRLeKzETmgI5EVVws9uZqmWEk1aVj24xgsukoUQlKuqQIRScjPWGnE6gKpbQw5bZh3wuf4gWzmGYmZcVnb--ogR40=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c130000597a9e5b_0%7C0a220b774c170000387ba921_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EQ8hU5rHthQDU2n1TYDLOmlpxsiKoF6JqGL4WFV-WeoJNcqOLXZZKpabkgoeSQlady_Y7pLMrQGdGyESO7pAjdZIlg_JEWmLtvt77V2J8iIm1_Bqve-a2_xbTDxxKcUeNnYp5x7SwPN4Pp86gihXC96vMeFbvMg5KPHVZDeKIKdNexEl_wPkSVMQDcZbHVhMGtcZm6z9b058JlspYs_Re7-vVgCPw1UuaEpJiibajOrFDHeGZsa18hEOhzzaXg5BY6XGvVO3fletuQG6rErZtrVSTn1h5zdH0uChYM2I7PFygRKVESCd_ZEV563th6gIvcrPpwRC_gldwtJjHMuQN0ee8RfbktLC1or5n0iHDmVGXjfwNT7WYlU4fxGrxvToqzdxTZ1pbTS0C96C3LAXonZ0pqQCeu1CeqYBXNAHfY6FhEbm85xlSaE8tutNdvmYBjiNsSBA5PrZU0DQ00l9w8qky1OC80AO8QTeQu17rXJP001_uugfyfyipz307w_-bBOBH4osNsw4LOc_lPjzZquiyzo8iCLZbLpVIP9bXkCEUEx5AwtIEE8IBimhX0K0MxhOQhZ-ZSSYmD5FJir-0X233Lbmw3CtHD8yGzUY9hN14XrXD0bQJgUh68kMFOT2lBauf9Gov23RdMehZ34kcl6uDMna02eL5KcQcH-z84DNEPvd7TNFc816Dd_uzc_AWW6Ey3Of7bTTGcPXfgVqRLeKzETmgI5EVVws9uZqmWEk1aVj24xgsukoUQlKuqQIRScjPWGnE6gKpbQw5bZh3wuf4gWzmGYmZcVnb--ogR40=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-04-28T19:45:00.000Z", "utc_arrival": "2023-04-28T17:45:00.000Z", "local_departure": "2023-04-28T16:15:00.000Z", "utc_departure": "2023-04-28T14:15:00.000Z"}, {"id": "0b770a224c2f0000d0b1f5bc_0|0a220b774c3200001b9f20d5_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 874.50106, "distance": 1975.87, "duration": {"departure": 12000, "return": 11700, "total": 23700}, "price": 275490.9193, "conversion": {"EUR": 721.16811, "HUF": 275490.9193}, "fare": {"adults": 137745.46, "children": 140502.24, "infants": 140502.24}, "bags_price": {"1": 72.282, "2": 144.564}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 6}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224c2f0000d0b1f5bc_0", "combination_id": "0b770a224c2f0000d0b1f5bc", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-26T21:45:00.000Z", "utc_arrival": "2023-05-26T19:45:00.000Z", "local_departure": "2023-05-26T18:25:00.000Z", "utc_departure": "2023-05-26T16:25:00.000Z"}, {"id": "0a220b774c3200001b9f20d5_0", "combination_id": "0a220b774c3200001b9f20d5", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "GREG", "fare_category": "M", "fare_classes": "G", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-29T23:45:00.000Z", "utc_arrival": "2023-05-29T21:45:00.000Z", "local_departure": "2023-05-29T20:30:00.000Z", "utc_departure": "2023-05-29T18:30:00.000Z"}], "booking_token": "Ehb26NlEygM7WD-dfwpApJ6w_kQ-VhrClywFN-RcVuavFRmuoiNcog59gtL_1QjceQ0QTedCNdW_I2dRK_H3t-mTJqILmCU_AXfl9InBTHea70QkP4augB53TeljhUvKqQUdaBDvs_F3rV_NT-ah683dLQBJ6Spv1LLQPBUEK7h8frPez6RvteuUtPHco-d02gaF5cjhiNQ1tV3vw-Rm-va6aXfQQO03IirJ8DX_6SyGr1aCyBBG8lvM6UUhxMmkyR68BKqD7XhH8FOijXoewx5rWm4qHZvS3wMgcdmG_yvf4C6RG_zRoVVoLuulqJFZrgSOFcIeuZ3MpA2KbLxoheThsf7HQtyvAVMwHEwaq_QhdsovRvV8lBdaQm9sx9dceUGsmhU6tefKtKOWOke84qqoYNnPcfHLa0-rRsOxrmGK_dOQ-KtBzWt_rjYqTsg1QI6M25u2cWSEDJ8cny5jIf4-gehJnXntG_-D09gHH8VF2yBFDZ9-hY3hCkF0RkQfYdGX_EexilUoVt_NG7zp3TuW2XVWxP7BCMsG36UBNwJlGv8kbtsdkFfYvyrYSUHpdNkowUUSlsMDs6q12jDyYbIJo35QUr185zRRhu0b2uh3z7ABQ3Fxg-_wHiS2uaT2wwo1u7qnw_8_zipBfsycCbad8ouk7cleQoCT1AVthN0GxHe4CYPyyzjVUwEONgy3oeFwxZRx5Z0tC6eL90cF0ox2m5lRu9GhZk2bsq20Ww7igEe8NW2x07fd4YxUu8Sdr_Y-bLHx2avMHzphOjO2t_A==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c2f0000d0b1f5bc_0%7C0a220b774c3200001b9f20d5_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=Ehb26NlEygM7WD-dfwpApJ6w_kQ-VhrClywFN-RcVuavFRmuoiNcog59gtL_1QjceQ0QTedCNdW_I2dRK_H3t-mTJqILmCU_AXfl9InBTHea70QkP4augB53TeljhUvKqQUdaBDvs_F3rV_NT-ah683dLQBJ6Spv1LLQPBUEK7h8frPez6RvteuUtPHco-d02gaF5cjhiNQ1tV3vw-Rm-va6aXfQQO03IirJ8DX_6SyGr1aCyBBG8lvM6UUhxMmkyR68BKqD7XhH8FOijXoewx5rWm4qHZvS3wMgcdmG_yvf4C6RG_zRoVVoLuulqJFZrgSOFcIeuZ3MpA2KbLxoheThsf7HQtyvAVMwHEwaq_QhdsovRvV8lBdaQm9sx9dceUGsmhU6tefKtKOWOke84qqoYNnPcfHLa0-rRsOxrmGK_dOQ-KtBzWt_rjYqTsg1QI6M25u2cWSEDJ8cny5jIf4-gehJnXntG_-D09gHH8VF2yBFDZ9-hY3hCkF0RkQfYdGX_EexilUoVt_NG7zp3TuW2XVWxP7BCMsG36UBNwJlGv8kbtsdkFfYvyrYSUHpdNkowUUSlsMDs6q12jDyYbIJo35QUr185zRRhu0b2uh3z7ABQ3Fxg-_wHiS2uaT2wwo1u7qnw_8_zipBfsycCbad8ouk7cleQoCT1AVthN0GxHe4CYPyyzjVUwEONgy3oeFwxZRx5Z0tC6eL90cF0ox2m5lRu9GhZk2bsq20Ww7igEe8NW2x07fd4YxUu8Sdr_Y-bLHx2avMHzphOjO2t_A==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-26T21:45:00.000Z", "utc_arrival": "2023-05-26T19:45:00.000Z", "local_departure": "2023-05-26T18:25:00.000Z", "utc_departure": "2023-05-26T16:25:00.000Z"}, {"id": "0b770a224c2b00006e021a7d_0|0a220b774c2f00005a82fb6a_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 882.630803, "distance": 1975.87, "duration": {"departure": 12600, "return": 12900, "total": 25500}, "price": 275540.4896, "conversion": {"EUR": 721.297873, "HUF": 275540.4896}, "fare": {"adults": 137770.24, "children": 140744, "infants": 140744}, "bags_price": {"1": 83.146, "2": 166.278}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 439, "hold_height": 149, "hold_length": 171, "hold_weight": 20, "hold_width": 119, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 5}, "airlines": ["W6"], "route": [{"id": "0b770a224c2b00006e021a7d_0", "combination_id": "0b770a224c2b00006e021a7d", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-22T19:45:00.000Z", "utc_arrival": "2023-05-22T17:45:00.000Z", "local_departure": "2023-05-22T16:15:00.000Z", "utc_departure": "2023-05-22T14:15:00.000Z"}, {"id": "0a220b774c2f00005a82fb6a_0", "combination_id": "0a220b774c2f00005a82fb6a", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "FREG", "fare_category": "M", "fare_classes": "F", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-27T00:05:00.000Z", "utc_arrival": "2023-05-26T22:05:00.000Z", "local_departure": "2023-05-26T20:30:00.000Z", "utc_departure": "2023-05-26T18:30:00.000Z"}], "booking_token": "EUX-jSrJ8-o2y9rR2UrDDLEn6xqTEWT3vh0JYsPoxEYZYWN0WvfCb85IILA3cnHw4l4tObJwYe0OfKNfL9agtjFJJWUQKpDDdc0WMguBAENaSQdvKDr5Tu2ZirnUBbMMSxSS3NUwhEtSPOmUlCMCcxbobkN9pX-OWMy8M2DUR3ZzOK9773lBZWmgW0O6GwX7pLVHMc04GAMlxwGXie_23a_xEvVJuF4siEy3IEToNT6F6wk6cp6xz_-4_2gRaBQF2uzo4fYncMIKc8QLF4cZaTmSw3VbY1HvQe-ZWTJh8adpzc0uxEBcJNUcrzfTZ54VH-0MPP1KUhx5j3kaml9N34R3yX78uLRGCtHH8ehjJT6-OFZ7DidUtQ9ndAB22Nz_oCQZlDzTw-P2kwpPRiUYc66JlvwDDVswGx_bkB6pLO-UTCiCrUjFDbopZvu-912rERZwSMAxrOtEA6_Uydak-SRSNc6OauUWdjPh2ohnCbJD6iCq8dQD9nEAiXLiN2pUbXtC1CkP4fBoM6qMBao-ddFAXVAaUBM7ZWIkYpes6dYled77W5ysoX6PN6unJVZBbt_AzkRSVG6qR9KhsFaQin2xk5XaOYXNmY5k6n1hdKsPjbdKoavh2hIusz9ZcISwasW8iU1UPvfcmnmg9hfZudZEENuvzynRAVjGCUgRIPtW0C0oxv3ZUryYRhdXO4Jhx18p3wPptZKY_zlPr45KjIW6WVt0sXtdPUDrNB1jGpbtw6Fm_4D5eYb34thYxvhYc8i30Dt0Ik6zxXmJ8_BBJY6iDLneRUWBaNH3jrXXoUWr_6ShZRUUpi5j41mQ_dXbi", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c2b00006e021a7d_0%7C0a220b774c2f00005a82fb6a_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EUX-jSrJ8-o2y9rR2UrDDLEn6xqTEWT3vh0JYsPoxEYZYWN0WvfCb85IILA3cnHw4l4tObJwYe0OfKNfL9agtjFJJWUQKpDDdc0WMguBAENaSQdvKDr5Tu2ZirnUBbMMSxSS3NUwhEtSPOmUlCMCcxbobkN9pX-OWMy8M2DUR3ZzOK9773lBZWmgW0O6GwX7pLVHMc04GAMlxwGXie_23a_xEvVJuF4siEy3IEToNT6F6wk6cp6xz_-4_2gRaBQF2uzo4fYncMIKc8QLF4cZaTmSw3VbY1HvQe-ZWTJh8adpzc0uxEBcJNUcrzfTZ54VH-0MPP1KUhx5j3kaml9N34R3yX78uLRGCtHH8ehjJT6-OFZ7DidUtQ9ndAB22Nz_oCQZlDzTw-P2kwpPRiUYc66JlvwDDVswGx_bkB6pLO-UTCiCrUjFDbopZvu-912rERZwSMAxrOtEA6_Uydak-SRSNc6OauUWdjPh2ohnCbJD6iCq8dQD9nEAiXLiN2pUbXtC1CkP4fBoM6qMBao-ddFAXVAaUBM7ZWIkYpes6dYled77W5ysoX6PN6unJVZBbt_AzkRSVG6qR9KhsFaQin2xk5XaOYXNmY5k6n1hdKsPjbdKoavh2hIusz9ZcISwasW8iU1UPvfcmnmg9hfZudZEENuvzynRAVjGCUgRIPtW0C0oxv3ZUryYRhdXO4Jhx18p3wPptZKY_zlPr45KjIW6WVt0sXtdPUDrNB1jGpbtw6Fm_4D5eYb34thYxvhYc8i30Dt0Ik6zxXmJ8_BBJY6iDLneRUWBaNH3jrXXoUWr_6ShZRUUpi5j41mQ_dXbi", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-22T19:45:00.000Z", "utc_arrival": "2023-05-22T17:45:00.000Z", "local_departure": "2023-05-22T16:15:00.000Z", "utc_departure": "2023-05-22T14:15:00.000Z"}, {"id": "0b770a224bfd00007895755b_0|0a220b774c00000072444fb5_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 882.147863, "distance": 1975.87, "duration": {"departure": 12600, "return": 11700, "total": 24300}, "price": 277393.3664, "conversion": {"EUR": 726.148253, "HUF": 277393.3664}, "fare": {"adults": 138696.68, "children": 138696.68, "infants": 138696.68}, "bags_price": {"1": 131.866, "2": 263.732}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 439, "hold_height": 149, "hold_length": 171, "hold_weight": 20, "hold_width": 119, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 2}, "airlines": ["W6"], "route": [{"id": "0b770a224bfd00007895755b_0", "combination_id": "0b770a224bfd00007895755b", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "GFREG", "fare_category": "M", "fare_classes": "G", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-06T21:15:00.000Z", "utc_arrival": "2023-04-06T19:15:00.000Z", "local_departure": "2023-04-06T17:45:00.000Z", "utc_departure": "2023-04-06T15:45:00.000Z"}, {"id": "0a220b774c00000072444fb5_0", "combination_id": "0a220b774c00000072444fb5", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "JREG", "fare_category": "M", "fare_classes": "J", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-09T21:05:00.000Z", "utc_arrival": "2023-04-09T19:05:00.000Z", "local_departure": "2023-04-09T17:50:00.000Z", "utc_departure": "2023-04-09T15:50:00.000Z"}], "booking_token": "EhrlTE8lZlAlSAElpmVZtl-QZ9wrNCp5nOeij8XpCw-ophc6thM3uShhW-JXDvIIIxKamYi5oOsbyZKsCqM-Pqm1IPqw_BjAmjLcH3xnydiM2UEmBxLkMS-_jQGroy3LDYWYhAbCzmsfIXVJ64w_KFxAPxgA2F7zt_0d-yAdQF03vdIlLT4UzCBs6WXz2HKsKrbZ5OMUniGoqID_RmQRK8qz8XMGqKbw5IrAiIyE9yKx4hGRo7A7vThaiLQzgwuzQ3Iy8JmvmDZBLcPXjVKANzD_mBFLHvAoU6HstF923H7GlopR4AQ3YBlMTEhGoMat4lpfHpHy2o23ayr2k3tgYXg7FP9E4NTPKHE6X5xFNCPEgv6MJIxZXxqhABQE9omcU6eQ7mw0-ve2ZmbTqz6f9gIl2r-AVRBAGqJum2GRd4mBCgGc_BRDccOAozoWCk2qJj5xPAvtAzqDBzbJqVurRkdVa3IWjb93KIYjjBSJM-8YeoQah0VfuQ5-R1Y_eFFOApHCpYwjcm32V5Ov0d0vcFJMnjrJ5MFjbdZZIqBngo-qrBIoSiA6eX03EwmzqUEd2JddTR3bdytrgRje5EWCYR4GsAeD8z5Z1ITqqVchfvqaWRaahAaxT79RIoK1qnn94ZsvqDMYFi538_A-dWEbWaL5NjKZYmfEfF_LSXWVKCcgwKyDgfXMfTV4YvPVylQXWkPWAZyzK9L7ER_v0eBalG6Qm1JA3t3FSbSNMgGkh8qZ2PnXtZT87eS9xEC-R7bqWh-s30F_ivRTnCUxwUZecCsfjVEAH25LB7l-WLLzNnBs=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224bfd00007895755b_0%7C0a220b774c00000072444fb5_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EhrlTE8lZlAlSAElpmVZtl-QZ9wrNCp5nOeij8XpCw-ophc6thM3uShhW-JXDvIIIxKamYi5oOsbyZKsCqM-Pqm1IPqw_BjAmjLcH3xnydiM2UEmBxLkMS-_jQGroy3LDYWYhAbCzmsfIXVJ64w_KFxAPxgA2F7zt_0d-yAdQF03vdIlLT4UzCBs6WXz2HKsKrbZ5OMUniGoqID_RmQRK8qz8XMGqKbw5IrAiIyE9yKx4hGRo7A7vThaiLQzgwuzQ3Iy8JmvmDZBLcPXjVKANzD_mBFLHvAoU6HstF923H7GlopR4AQ3YBlMTEhGoMat4lpfHpHy2o23ayr2k3tgYXg7FP9E4NTPKHE6X5xFNCPEgv6MJIxZXxqhABQE9omcU6eQ7mw0-ve2ZmbTqz6f9gIl2r-AVRBAGqJum2GRd4mBCgGc_BRDccOAozoWCk2qJj5xPAvtAzqDBzbJqVurRkdVa3IWjb93KIYjjBSJM-8YeoQah0VfuQ5-R1Y_eFFOApHCpYwjcm32V5Ov0d0vcFJMnjrJ5MFjbdZZIqBngo-qrBIoSiA6eX03EwmzqUEd2JddTR3bdytrgRje5EWCYR4GsAeD8z5Z1ITqqVchfvqaWRaahAaxT79RIoK1qnn94ZsvqDMYFi538_A-dWEbWaL5NjKZYmfEfF_LSXWVKCcgwKyDgfXMfTV4YvPVylQXWkPWAZyzK9L7ER_v0eBalG6Qm1JA3t3FSbSNMgGkh8qZ2PnXtZT87eS9xEC-R7bqWh-s30F_ivRTnCUxwUZecCsfjVEAH25LB7l-WLLzNnBs=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-04-06T21:15:00.000Z", "utc_arrival": "2023-04-06T19:15:00.000Z", "local_departure": "2023-04-06T17:45:00.000Z", "utc_departure": "2023-04-06T15:45:00.000Z"}, {"id": "0b770a224c2c0000f97822f4_0|0a220b774c2f00005a82fb6a_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 891.989233, "distance": 1975.87, "duration": {"departure": 12000, "return": 12900, "total": 24900}, "price": 280134.1524, "conversion": {"EUR": 733.322963, "HUF": 280134.1524}, "fare": {"adults": 140067.08, "children": 140067.08, "infants": 140067.08}, "bags_price": {"1": 70, "2": 140.014}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 5}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224c2c0000f97822f4_0", "combination_id": "0b770a224c2c0000f97822f4", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-23T10:15:00.000Z", "utc_arrival": "2023-05-23T08:15:00.000Z", "local_departure": "2023-05-23T06:55:00.000Z", "utc_departure": "2023-05-23T04:55:00.000Z"}, {"id": "0a220b774c2f00005a82fb6a_0", "combination_id": "0a220b774c2f00005a82fb6a", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "FREG", "fare_category": "M", "fare_classes": "F", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-27T00:05:00.000Z", "utc_arrival": "2023-05-26T22:05:00.000Z", "local_departure": "2023-05-26T20:30:00.000Z", "utc_departure": "2023-05-26T18:30:00.000Z"}], "booking_token": "E7WcxUmH607U8UYyPxwbXYBdKMTvcT5fns2RwfwMQu0cqic5GsDo0sTfBUNlincKRlYDYH_Ru9BZf8AqVcmd6Hvvwzk-krbHaVF_MgPlWUn_sWePH-LvtwCg8Z-GZwTRrU5AWJGQ_BA7FQ0bb2kjSHY2U5PMROn7yZCd4SfOkLrV0PnV_dWXfK76YEhKcBgqSAZl02-lPe2vLWZ3nDf9zlzOG2odn0kgmz9bVClfdPsWxvVVK942UlxVwA35SQxHcXssl8j29glhqguZDR3dI4m4dJe7q-YZY8dQJvxS4vT2CH91J4z-sxhLAASs9WMPZD1rHghncQ7h0Etc2SbN6N06t5Gf_ghrVE0oOGKJIuABYVfaAC9ymc1sP38bVGtqhynAAjUY4bvnSBGf4caiXjr8XRn8hHP2xbswoqu0AZs4v4NSDt7idCyDIgWm6tmCsfVvnMT43Q0ZwghNHynWqRTOaAhpdKC8O9JOBwd39qNBagOmfZxlnRHqYBtxGCnyA_ZSvS1alnCnFPtufZ-SSTI6Dl8aJioUUbPEaZ4oJR8npXpG1A-p_AJip_iXQcXqMb5S63-yUESn_EotA8cRpB02nINt7df_-PaN5bv9ejEGPLrkUC6AeZN6hupFAKFDQBJZEjYEr21SOaSFso_epNVxiNhvc6B5WEFKZW34CM-vcpU1ttXI0VM-Ain-GjaN_KLYhhanUgYanwWZDz1eRTqgCamjkP3x4vedCGDjf4bBm5Tpkg-2TgAc2SAPntCD75lC-B9Ru_DdKfwMXCTBfHA==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c2c0000f97822f4_0%7C0a220b774c2f00005a82fb6a_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=E7WcxUmH607U8UYyPxwbXYBdKMTvcT5fns2RwfwMQu0cqic5GsDo0sTfBUNlincKRlYDYH_Ru9BZf8AqVcmd6Hvvwzk-krbHaVF_MgPlWUn_sWePH-LvtwCg8Z-GZwTRrU5AWJGQ_BA7FQ0bb2kjSHY2U5PMROn7yZCd4SfOkLrV0PnV_dWXfK76YEhKcBgqSAZl02-lPe2vLWZ3nDf9zlzOG2odn0kgmz9bVClfdPsWxvVVK942UlxVwA35SQxHcXssl8j29glhqguZDR3dI4m4dJe7q-YZY8dQJvxS4vT2CH91J4z-sxhLAASs9WMPZD1rHghncQ7h0Etc2SbN6N06t5Gf_ghrVE0oOGKJIuABYVfaAC9ymc1sP38bVGtqhynAAjUY4bvnSBGf4caiXjr8XRn8hHP2xbswoqu0AZs4v4NSDt7idCyDIgWm6tmCsfVvnMT43Q0ZwghNHynWqRTOaAhpdKC8O9JOBwd39qNBagOmfZxlnRHqYBtxGCnyA_ZSvS1alnCnFPtufZ-SSTI6Dl8aJioUUbPEaZ4oJR8npXpG1A-p_AJip_iXQcXqMb5S63-yUESn_EotA8cRpB02nINt7df_-PaN5bv9ejEGPLrkUC6AeZN6hupFAKFDQBJZEjYEr21SOaSFso_epNVxiNhvc6B5WEFKZW34CM-vcpU1ttXI0VM-Ain-GjaN_KLYhhanUgYanwWZDz1eRTqgCamjkP3x4vedCGDjf4bBm5Tpkg-2TgAc2SAPntCD75lC-B9Ru_DdKfwMXCTBfHA==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-23T10:15:00.000Z", "utc_arrival": "2023-05-23T08:15:00.000Z", "local_departure": "2023-05-23T06:55:00.000Z", "utc_departure": "2023-05-23T04:55:00.000Z"}, {"id": "0b770a224c0800004ab681ca_0|0a220b774c0b00004bb09d25_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 887.248926, "distance": 1975.87, "duration": {"departure": 12000, "return": 11700, "total": 23700}, "price": 280360.6872, "conversion": {"EUR": 733.915976, "HUF": 280360.6872}, "fare": {"adults": 140180.34, "children": 143104.91, "infants": 143104.91}, "bags_price": {"1": 97.706, "2": 195.412}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 6}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224c0800004ab681ca_0", "combination_id": "0b770a224c0800004ab681ca", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-17T14:00:00.000Z", "utc_arrival": "2023-04-17T12:00:00.000Z", "local_departure": "2023-04-17T10:40:00.000Z", "utc_departure": "2023-04-17T08:40:00.000Z"}, {"id": "0a220b774c0b00004bb09d25_0", "combination_id": "0a220b774c0b00004bb09d25", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "HIREG", "fare_category": "M", "fare_classes": "H", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-21T01:15:00.000Z", "utc_arrival": "2023-04-20T23:15:00.000Z", "local_departure": "2023-04-20T22:00:00.000Z", "utc_departure": "2023-04-20T20:00:00.000Z"}], "booking_token": "E-zToOkUUwleuiKStYovZkx5nCGBa9tq3CtNIHmSBXmemxal_MVfNoNCl19BdxQumcRKzRC90gvzRzxPHjRCMCt29tjZNE5q-IE8nqz1lFNobrBzAbgcRMqXnVm30Jux_PPuep_GlzW4iuLPtT2kNbH9akiC106FLj3Tzc7dk-m_8YMYhWtf1zFIjKe79Bo6uF5yzU2uWcqJ-AXOQGcFoKPs9-uJBrrVbcwsrevNJkPOrFL7E2difZA93hAVcWG7u23JyUFy7Rv-MATv2fmoTGxBmDRig28r6mSDdgCK57C3evDRBHN2zYcmF8hhwBmAeeIDbYOiaUJ4_a5dGlLMeIiBZ-YijccZx6e5cUW9VKO5jLin0rStkFNZe7ini3lLbG7sLHaumvzu1X0k6BMMIiYqoLD8W_rECHaBVXQssTTbjlSa0BTT78sTD6bDiIYuxphuAjHoDVJCmTvALdthhkI91SU8ZS8nwwbli9ShySsycx7LLcJhnCyVL6zUtJ_xXeIqSdvIxUc7HsCGYjLph8sLfpYTYLLtvTPg5PwN0nNzIk3CIl9FI3XV8dWPebo4Qibawr5mxCCr1umdkyN72IL5EoXLW0CJdphyrqfgdMccZ8bo-s9ilumJ9ykUleQJVepsw9twfd4EsRugzXbxR6-9e0rX5fydPskArItAM_oQSUdE29GN-beTI-iGlKX19AqO1IHWQ3gECLBLiYhUh9vmJ7pI7EbrsnihK0-Ao7iBevRPJVI22n-BvIrlJa-dopEoEmXh0GjF3kJ3-MrTqVw==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c0800004ab681ca_0%7C0a220b774c0b00004bb09d25_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=E-zToOkUUwleuiKStYovZkx5nCGBa9tq3CtNIHmSBXmemxal_MVfNoNCl19BdxQumcRKzRC90gvzRzxPHjRCMCt29tjZNE5q-IE8nqz1lFNobrBzAbgcRMqXnVm30Jux_PPuep_GlzW4iuLPtT2kNbH9akiC106FLj3Tzc7dk-m_8YMYhWtf1zFIjKe79Bo6uF5yzU2uWcqJ-AXOQGcFoKPs9-uJBrrVbcwsrevNJkPOrFL7E2difZA93hAVcWG7u23JyUFy7Rv-MATv2fmoTGxBmDRig28r6mSDdgCK57C3evDRBHN2zYcmF8hhwBmAeeIDbYOiaUJ4_a5dGlLMeIiBZ-YijccZx6e5cUW9VKO5jLin0rStkFNZe7ini3lLbG7sLHaumvzu1X0k6BMMIiYqoLD8W_rECHaBVXQssTTbjlSa0BTT78sTD6bDiIYuxphuAjHoDVJCmTvALdthhkI91SU8ZS8nwwbli9ShySsycx7LLcJhnCyVL6zUtJ_xXeIqSdvIxUc7HsCGYjLph8sLfpYTYLLtvTPg5PwN0nNzIk3CIl9FI3XV8dWPebo4Qibawr5mxCCr1umdkyN72IL5EoXLW0CJdphyrqfgdMccZ8bo-s9ilumJ9ykUleQJVepsw9twfd4EsRugzXbxR6-9e0rX5fydPskArItAM_oQSUdE29GN-beTI-iGlKX19AqO1IHWQ3gECLBLiYhUh9vmJ7pI7EbrsnihK0-Ao7iBevRPJVI22n-BvIrlJa-dopEoEmXh0GjF3kJ3-MrTqVw==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-04-17T14:00:00.000Z", "utc_arrival": "2023-04-17T12:00:00.000Z", "local_departure": "2023-04-17T10:40:00.000Z", "utc_departure": "2023-04-17T08:40:00.000Z"}, {"id": "0b770a224be700000fa7ada1_0|0a220b774beb0000ffe2d784_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 888.624412, "distance": 1975.87, "duration": {"departure": 12000, "return": 11700, "total": 23700}, "price": 280886.1318, "conversion": {"EUR": 735.291462, "HUF": 280886.1318}, "fare": {"adults": 140443.07, "children": 140443.07, "infants": 140443.07}, "bags_price": {"1": 90.972, "2": 181.944}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 3}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224be700000fa7ada1_0", "combination_id": "0b770a224be700000fa7ada1", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-03-15T23:20:00.000Z", "utc_arrival": "2023-03-15T22:20:00.000Z", "local_departure": "2023-03-15T20:00:00.000Z", "utc_departure": "2023-03-15T19:00:00.000Z"}, {"id": "0a220b774beb0000ffe2d784_0", "combination_id": "0a220b774beb0000ffe2d784", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "HREG", "fare_category": "M", "fare_classes": "H", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-03-19T21:45:00.000Z", "utc_arrival": "2023-03-19T20:45:00.000Z", "local_departure": "2023-03-19T18:30:00.000Z", "utc_departure": "2023-03-19T17:30:00.000Z"}], "booking_token": "EBx49oBtzybKP9M1G-mMrwboQEQEcZLprPcpUtS0eZDbGVNuVIACes6OXDqkvYFcIM_WjOIuFWcsa_jcN2YSxgC1iUS7W7MgyB3Ctw-kKgfY_1PNiWwsAy9j6B0r0I8HLgcJSURfygClF7zSOsZ6zhzetXDSWAf_Dt88QRWEPzU6qgeldvXG_zrlf4lpfxxlepfv77wjNR8T-l_zbTw23mKZ7D76KdOYXPCZzvxL_J9bZeFGdWZheZvTa41r5HDpbVw7u7mrfuPbjcTBFyaitpw3eC-x_wlcWyTz_9QxN8laq7aZGMGGvo0w-X1eDSHIyCWPz35DvxPTIkjQ_2MCdZchhgxVgpWnM67NEqyUeV8z30jryD0AETnINswyzZBWxNBmc-V4tthdL3uZOnvCVPe5_87vNZ15qeSCD48RLYiXxcf7DvdpaVu0dNjQEpHxihA6TXivElmA9DrxZMAO5kPAjt8jnNHOBZb3T8sB4S6hrA90chXaz8I_NeHhs8qc7nPjyAbCRXIcqx5JWRvskECtiFZ_SSIx5Omg9hq1MialBPSj0WapB57Lm088Zxh4dIN0UMSPbbdCZb3iUSHQ0GLNqX-xNonw-E5tyoHs-dXYSHJHNUpvvu5wPmoAhtk4vJ9LW0_X_BOFh1p3LUIpvTNzRvLnoGdz6Yjw2DxiqALLerhn2LriHI3JqIYUTbcDGPsFwvmGkrgR7a9DIqigt2jNlkmwDvA4kvRVhNkNVf2HU_l_7_3b7YME1Hw01bcI1YDNtiy90wzaMzZKZZcfPAVaWstatDj-hGviAp5f9dUT0xfduTO2b0jRIJNJXFLyT", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224be700000fa7ada1_0%7C0a220b774beb0000ffe2d784_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EBx49oBtzybKP9M1G-mMrwboQEQEcZLprPcpUtS0eZDbGVNuVIACes6OXDqkvYFcIM_WjOIuFWcsa_jcN2YSxgC1iUS7W7MgyB3Ctw-kKgfY_1PNiWwsAy9j6B0r0I8HLgcJSURfygClF7zSOsZ6zhzetXDSWAf_Dt88QRWEPzU6qgeldvXG_zrlf4lpfxxlepfv77wjNR8T-l_zbTw23mKZ7D76KdOYXPCZzvxL_J9bZeFGdWZheZvTa41r5HDpbVw7u7mrfuPbjcTBFyaitpw3eC-x_wlcWyTz_9QxN8laq7aZGMGGvo0w-X1eDSHIyCWPz35DvxPTIkjQ_2MCdZchhgxVgpWnM67NEqyUeV8z30jryD0AETnINswyzZBWxNBmc-V4tthdL3uZOnvCVPe5_87vNZ15qeSCD48RLYiXxcf7DvdpaVu0dNjQEpHxihA6TXivElmA9DrxZMAO5kPAjt8jnNHOBZb3T8sB4S6hrA90chXaz8I_NeHhs8qc7nPjyAbCRXIcqx5JWRvskECtiFZ_SSIx5Omg9hq1MialBPSj0WapB57Lm088Zxh4dIN0UMSPbbdCZb3iUSHQ0GLNqX-xNonw-E5tyoHs-dXYSHJHNUpvvu5wPmoAhtk4vJ9LW0_X_BOFh1p3LUIpvTNzRvLnoGdz6Yjw2DxiqALLerhn2LriHI3JqIYUTbcDGPsFwvmGkrgR7a9DIqigt2jNlkmwDvA4kvRVhNkNVf2HU_l_7_3b7YME1Hw01bcI1YDNtiy90wzaMzZKZZcfPAVaWstatDj-hGviAp5f9dUT0xfduTO2b0jRIJNJXFLyT", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-03-15T23:20:00.000Z", "utc_arrival": "2023-03-15T22:20:00.000Z", "local_departure": "2023-03-15T20:00:00.000Z", "utc_departure": "2023-03-15T19:00:00.000Z"}, {"id": "0b770a224c350000fd39ce98_0|0a220b774c380000a326b971_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 894.212013, "distance": 1975.87, "duration": {"departure": 12600, "return": 11700, "total": 24300}, "price": 282001.9504, "conversion": {"EUR": 738.212403, "HUF": 282001.9504}, "fare": {"adults": 141000.98, "children": 141000.98, "infants": 141000.98}, "bags_price": {"1": 115.976, "2": 231.966}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 439, "hold_height": 149, "hold_length": 171, "hold_weight": 20, "hold_width": 119, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 3}, "airlines": ["W6"], "route": [{"id": "0b770a224c350000fd39ce98_0", "combination_id": "0b770a224c350000fd39ce98", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "HREG", "fare_category": "M", "fare_classes": "H", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-01T21:15:00.000Z", "utc_arrival": "2023-06-01T19:15:00.000Z", "local_departure": "2023-06-01T17:45:00.000Z", "utc_departure": "2023-06-01T15:45:00.000Z"}, {"id": "0a220b774c380000a326b971_0", "combination_id": "0a220b774c380000a326b971", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "GREG", "fare_category": "M", "fare_classes": "G", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-04T21:05:00.000Z", "utc_arrival": "2023-06-04T19:05:00.000Z", "local_departure": "2023-06-04T17:50:00.000Z", "utc_departure": "2023-06-04T15:50:00.000Z"}], "booking_token": "EKpN_IEV00d73wFwJVDvWcQuCR5TtUUyKIV0Xn5htLMBNwnBkFs8h4kqcontx-bAs7vsyBQSOa32qpACH7QdmBedIdjKnIY2QHNzROpwtVgX8KU7AQXT5JDAnEoXRKNuO7KToIa9-DT1OLs3GZI_YiadmU1YNj6chdSvGtzCUD0xT_wgJWzSYAts8HJZMhC1K_h5H3_bxX7RWW9vfvlhj8bB-riFHdmPjmVLVVrt9irL09NU9n6GL_tLImF2FJ8eke6vLjEUyMjGRuQ7Vbyvnnbbk3Sfsvsu0Myv2_-0Y7T9ZQqoQpNVpEFFbqp_HPf-CctdlQI1s3dRT8v6RsAXiHxBmYEFt_I6OIKxM2KXjpdPhZhg1P85ZC5Pcg1KS-Qp7_2Sq7pnIH_48dtyeU1JERbtzu43qpRk4XsUroURtfkdEuctaM4RmMFdQNTVRxNTxkxHy6dOCFWPO4vQlFy5uu8OPEZh9sNVRUZd2AAoqOLIAn8SNxKo1u8DBLYRvb6SHNqkQOPOQjR2aeKGavJRhPNkYgHlM4rrO5TjbFBR_TXS0IHpwBddskMIz4DqVliXC07G2YLgPpQ8GpWX7phQTpPsdakFyG-vdr3nX8ePbAuzZa9j3Gk3Y-biYNjQm40VxQGS0vBZymOSFg8Vy41TtHEtBlzduqfV9QlXChOgZClRj95nHlRci9SmbrS77k66a2WVc7MsFE1jbNFkCYyEmOZH0vWIv9if2_Bdn1ZwGhEVeiX9tabTixEG96MVP25GBe_Jmp_ioTPSi8nNvpfI_Ng==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c350000fd39ce98_0%7C0a220b774c380000a326b971_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EKpN_IEV00d73wFwJVDvWcQuCR5TtUUyKIV0Xn5htLMBNwnBkFs8h4kqcontx-bAs7vsyBQSOa32qpACH7QdmBedIdjKnIY2QHNzROpwtVgX8KU7AQXT5JDAnEoXRKNuO7KToIa9-DT1OLs3GZI_YiadmU1YNj6chdSvGtzCUD0xT_wgJWzSYAts8HJZMhC1K_h5H3_bxX7RWW9vfvlhj8bB-riFHdmPjmVLVVrt9irL09NU9n6GL_tLImF2FJ8eke6vLjEUyMjGRuQ7Vbyvnnbbk3Sfsvsu0Myv2_-0Y7T9ZQqoQpNVpEFFbqp_HPf-CctdlQI1s3dRT8v6RsAXiHxBmYEFt_I6OIKxM2KXjpdPhZhg1P85ZC5Pcg1KS-Qp7_2Sq7pnIH_48dtyeU1JERbtzu43qpRk4XsUroURtfkdEuctaM4RmMFdQNTVRxNTxkxHy6dOCFWPO4vQlFy5uu8OPEZh9sNVRUZd2AAoqOLIAn8SNxKo1u8DBLYRvb6SHNqkQOPOQjR2aeKGavJRhPNkYgHlM4rrO5TjbFBR_TXS0IHpwBddskMIz4DqVliXC07G2YLgPpQ8GpWX7phQTpPsdakFyG-vdr3nX8ePbAuzZa9j3Gk3Y-biYNjQm40VxQGS0vBZymOSFg8Vy41TtHEtBlzduqfV9QlXChOgZClRj95nHlRci9SmbrS77k66a2WVc7MsFE1jbNFkCYyEmOZH0vWIv9if2_Bdn1ZwGhEVeiX9tabTixEG96MVP25GBe_Jmp_ioTPSi8nNvpfI_Ng==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-01T21:15:00.000Z", "utc_arrival": "2023-06-01T19:15:00.000Z", "local_departure": "2023-06-01T17:45:00.000Z", "utc_departure": "2023-06-01T15:45:00.000Z"}, {"id": "0b770a224c120000d0b8a626_0|0a220b774c1600007449e031_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 902.440156, "distance": 1975.87, "duration": {"departure": 12600, "return": 11400, "total": 24000}, "price": 285654.4954, "conversion": {"EUR": 747.773876, "HUF": 285654.4954}, "fare": {"adults": 142827.25, "children": 142827.25, "infants": 142827.25}, "bags_price": {"1": 106.862, "2": 213.738}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 4}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224c120000d0b8a626_0", "combination_id": "0b770a224c120000d0b8a626", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "HREG", "fare_category": "M", "fare_classes": "H", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-27T21:15:00.000Z", "utc_arrival": "2023-04-27T19:15:00.000Z", "local_departure": "2023-04-27T17:45:00.000Z", "utc_departure": "2023-04-27T15:45:00.000Z"}, {"id": "0a220b774c1600007449e031_0", "combination_id": "0a220b774c1600007449e031", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-01T10:15:00.000Z", "utc_arrival": "2023-05-01T08:15:00.000Z", "local_departure": "2023-05-01T07:05:00.000Z", "utc_departure": "2023-05-01T05:05:00.000Z"}], "booking_token": "EFgEH4f6df0hzLSLuy70jE-UtZccAj8TyPXTl6_d10_lrIw7h4ZAA80fROz9CSV4uefHYBj5VVpqwSzIQtTfxlvGkeQJMkUaq2I5JRI8bYVpN9QTSAtpdeLyfNWRlexK5TcgcXYik_y2jX2EXhJGh5G8QOBa2kgotpGDTGyrUEgC3JfAwUwOlPnfYB-1qPCcFZG6W5CRUuBbP6uPm-Rakj-KeYprTZIcgkdmEl3sguIa4kbWJUb-OHNiYQ8p5_aT41Vu0sMKNRPZyOC_2DqCWg-6NqNSzXE-F_aR-HHrrhM9uzDxwQeOYINh8RQYGt4eRlzoT517H8FZbjzWswv9rkpyWYzB1ujoF6ioXMUVElirOekwu9BY5Fp7_tqGNFGDBcMmCa7EjbPllFwMAkjHYIUvuvtQx4frzXZxMOjkypSmConIeP-Q6Y21pwJSTZU5X96SsJJVwCRay-p4tkqfMd0ggTd8KUw6P5TLWWxyeM5X2HNdOiq4vn20k4Jx1ehNvR8NfchY3eubAfKKS5jYvVGyNKETKG0r4TzstSuDu7hB3DTDhazqTc21XYDjTf5oSmzsdag7h64MfpZYbbr-c-HDVmXPfkkyzOe45_nRazwd3C6lVCTYDUGS1cb-N27u9tGpk0xEdtOp_2NY1nmFS31j3aUwYU1Qx3p67TVzmIgQdco0L7qtlJz1eD2i8WWa0wpF_5TJMObCH00nISZAjiBZd8HxhViHhf-aFQoT-v3yiqTKDM1kJ5naUNbUgwEtEsrdWkN0hqx4_syCEZ7pepw==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c120000d0b8a626_0%7C0a220b774c1600007449e031_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EFgEH4f6df0hzLSLuy70jE-UtZccAj8TyPXTl6_d10_lrIw7h4ZAA80fROz9CSV4uefHYBj5VVpqwSzIQtTfxlvGkeQJMkUaq2I5JRI8bYVpN9QTSAtpdeLyfNWRlexK5TcgcXYik_y2jX2EXhJGh5G8QOBa2kgotpGDTGyrUEgC3JfAwUwOlPnfYB-1qPCcFZG6W5CRUuBbP6uPm-Rakj-KeYprTZIcgkdmEl3sguIa4kbWJUb-OHNiYQ8p5_aT41Vu0sMKNRPZyOC_2DqCWg-6NqNSzXE-F_aR-HHrrhM9uzDxwQeOYINh8RQYGt4eRlzoT517H8FZbjzWswv9rkpyWYzB1ujoF6ioXMUVElirOekwu9BY5Fp7_tqGNFGDBcMmCa7EjbPllFwMAkjHYIUvuvtQx4frzXZxMOjkypSmConIeP-Q6Y21pwJSTZU5X96SsJJVwCRay-p4tkqfMd0ggTd8KUw6P5TLWWxyeM5X2HNdOiq4vn20k4Jx1ehNvR8NfchY3eubAfKKS5jYvVGyNKETKG0r4TzstSuDu7hB3DTDhazqTc21XYDjTf5oSmzsdag7h64MfpZYbbr-c-HDVmXPfkkyzOe45_nRazwd3C6lVCTYDUGS1cb-N27u9tGpk0xEdtOp_2NY1nmFS31j3aUwYU1Qx3p67TVzmIgQdco0L7qtlJz1eD2i8WWa0wpF_5TJMObCH00nISZAjiBZd8HxhViHhf-aFQoT-v3yiqTKDM1kJ5naUNbUgwEtEsrdWkN0hqx4_syCEZ7pepw==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-04-27T21:15:00.000Z", "utc_arrival": "2023-04-27T19:15:00.000Z", "local_departure": "2023-04-27T17:45:00.000Z", "utc_departure": "2023-04-27T15:45:00.000Z"}, {"id": "0b770a224c4d00007b45914b_0|0a220b774c51000099b168e7_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 909.307909, "distance": 1975.87, "duration": {"departure": 12600, "return": 11700, "total": 24300}, "price": 287768.681, "conversion": {"EUR": 753.308299, "HUF": 287768.681}, "fare": {"adults": 143884.34, "children": 143884.34, "infants": 143884.34}, "bags_price": {"1": 123.424, "2": 246.834}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 439, "hold_height": 149, "hold_length": 171, "hold_weight": 20, "hold_width": 119, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 3}, "airlines": ["W6"], "route": [{"id": "0b770a224c4d00007b45914b_0", "combination_id": "0b770a224c4d00007b45914b", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "FEREG", "fare_category": "M", "fare_classes": "F", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-25T17:05:00.000Z", "utc_arrival": "2023-06-25T15:05:00.000Z", "local_departure": "2023-06-25T13:35:00.000Z", "utc_departure": "2023-06-25T11:35:00.000Z"}, {"id": "0a220b774c51000099b168e7_0", "combination_id": "0a220b774c51000099b168e7", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IJREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-30T01:15:00.000Z", "utc_arrival": "2023-06-29T23:15:00.000Z", "local_departure": "2023-06-29T22:00:00.000Z", "utc_departure": "2023-06-29T20:00:00.000Z"}], "booking_token": "Eyd510oNcCBn5qZs8FH0fDQlH76Ox2QugNYLVun7VOuCVTfTBVNqS5vEvtAg-Ux0jlBZGaXUTnt6Rp_jA27k3aJ7BayyOwRXRWONOLcNOfFKll2TKkjY3wAMFYHKOQoDtboR_0x-rCSXknHDM6i12OYIMTffVCLVSzccJ3wgtpY438oUR1HEAdyg-k2c3GYdWYlxKYL6dka_Ac-98ArXm-wVzDfUhmuKs3hB9QV2wocRHzGz7k9OxzUyT0TnWZzhj2LYoWNAMR7McoF8SXDDGSzn2s1qze4JH2OiHRzRiray4diHY4TwzH0V3S-s1auivAaCraXNEwUZcKp3IFKPHH-oGJV-X57FQRzxC6yoaa9jk5aGbi8GI4VFmCVrtGYy-OGnSRUB1_FYk3_QOt-AGZmrAY-lpTmrd2faYHp4w334BEMt1G5rpCgQRJMMsTt7tzc_ah27sAqxACeS43kdG0IaCBSca6V_xK9g2nPjnX5v7TVIWQEmEZegmOEWBqBYdnmi9SfzCVHyb5J9KO1T9yyb_NivUmexFS0fYOq3pHl9-UjD2ql2RzBttVpSN447p5cgdlhaUuh-ME6V9sOH1Lhn3DVcPv7PGUOpgb8gM7zQDtWjGoOS6MLDLiffqiy5Q8X_iaystMjiJ2d2G6X03PXzjldbcz1akWbjhZ1rondcSuLZbG6CFsmtKBf4zf-KiEZ1dStwqEP0n_SA903iih1WthC-fk-yoN8izAxmHFxqbSBZOQoZ7RDDzlA5ixquszaNqA0dv26hAVCB10hfOpJdZL1xgG9wKllbXdBpHLOc=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c4d00007b45914b_0%7C0a220b774c51000099b168e7_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=Eyd510oNcCBn5qZs8FH0fDQlH76Ox2QugNYLVun7VOuCVTfTBVNqS5vEvtAg-Ux0jlBZGaXUTnt6Rp_jA27k3aJ7BayyOwRXRWONOLcNOfFKll2TKkjY3wAMFYHKOQoDtboR_0x-rCSXknHDM6i12OYIMTffVCLVSzccJ3wgtpY438oUR1HEAdyg-k2c3GYdWYlxKYL6dka_Ac-98ArXm-wVzDfUhmuKs3hB9QV2wocRHzGz7k9OxzUyT0TnWZzhj2LYoWNAMR7McoF8SXDDGSzn2s1qze4JH2OiHRzRiray4diHY4TwzH0V3S-s1auivAaCraXNEwUZcKp3IFKPHH-oGJV-X57FQRzxC6yoaa9jk5aGbi8GI4VFmCVrtGYy-OGnSRUB1_FYk3_QOt-AGZmrAY-lpTmrd2faYHp4w334BEMt1G5rpCgQRJMMsTt7tzc_ah27sAqxACeS43kdG0IaCBSca6V_xK9g2nPjnX5v7TVIWQEmEZegmOEWBqBYdnmi9SfzCVHyb5J9KO1T9yyb_NivUmexFS0fYOq3pHl9-UjD2ql2RzBttVpSN447p5cgdlhaUuh-ME6V9sOH1Lhn3DVcPv7PGUOpgb8gM7zQDtWjGoOS6MLDLiffqiy5Q8X_iaystMjiJ2d2G6X03PXzjldbcz1akWbjhZ1rondcSuLZbG6CFsmtKBf4zf-KiEZ1dStwqEP0n_SA903iih1WthC-fk-yoN8izAxmHFxqbSBZOQoZ7RDDzlA5ixquszaNqA0dv26hAVCB10hfOpJdZL1xgG9wKllbXdBpHLOc=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-25T17:05:00.000Z", "utc_arrival": "2023-06-25T15:05:00.000Z", "local_departure": "2023-06-25T13:35:00.000Z", "utc_departure": "2023-06-25T11:35:00.000Z"}, {"id": "0b770a224bf60000a70051c8_0|0a220b774bfa0000932c3671_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 912.12823, "distance": 1975.87, "duration": {"departure": 12600, "return": 11400, "total": 24000}, "price": 289355.4028, "conversion": {"EUR": 757.46195, "HUF": 289355.4028}, "fare": {"adults": 144677.7, "children": 153101.44, "infants": 153101.44}, "bags_price": {"1": 112.882, "2": 197.078}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": null}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224bf60000a70051c8_0", "combination_id": "0b770a224bf60000a70051c8", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "JKREG", "fare_category": "M", "fare_classes": "J", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-03-30T21:15:00.000Z", "utc_arrival": "2023-03-30T19:15:00.000Z", "local_departure": "2023-03-30T17:45:00.000Z", "utc_departure": "2023-03-30T15:45:00.000Z"}, {"id": "0a220b774bfa0000932c3671_0", "combination_id": "0a220b774bfa0000932c3671", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-03T10:15:00.000Z", "utc_arrival": "2023-04-03T08:15:00.000Z", "local_departure": "2023-04-03T07:05:00.000Z", "utc_departure": "2023-04-03T05:05:00.000Z"}], "booking_token": "E56ea0HvIMJJMw2mUun5THETKbmAH82UvgXrS90ou0st1zRYqVE3FWkJaUezJKtIedfacC6pNk_ssXI5WgsbcfVzFMSLpaxxHY-EsccMdaLmrPCqeD6-R3ZEKiRR0oaxKYia05xlNkaaGqTfeLtfQqTUiaDXlk8LwD9sAAv9LmNhNw4wGWYLiJNCRy93q1AF4eYUGKMDwQxC37ePe0IOe7kLRdwRGwZ8_4IcZKcOlbFo6m1HFJY3GevJithbxV16l3pfOzuhGiP4jwT6iMGX-W6JYfbCcpZ-B_yKDuhRkapIhm3KNhlv3jAVe8NmHjAP8gfBdcK2enTtjyQZmUJNrd63ZDYY2XE0Lftcn9GpuXDYghsEWvWX5E7328d69PsX23C5YJDUPFGA134DatJxKVUEdf4JeP_uB4ZJt06iw83N2Ddgt_M4bOuvC0YsTyP4Nn7Xuz3Fgb7IPwA9ypFhof1gx_J_KXaG_Q0yvbYuDoCyoOtbFH91C9VmX0jhWf3x7FJjmYy2f00gsLdBBXbtg84IpD8B24XkLPM-4K8JHkIDaOM3jMjTHvbUXtiyxUmfeAznejeoiYWf7RvEHD-ZnpCP4-BZqwkBDBuvQUe5a7CaN2Do0a9UhlF50RvsVK0ZKFLrwrlsItcvUSbefIh_TzHWP1ODxzuogJa05g7Wwz4hlytAeQEp4XiXw11KDDTZ8fAFzcZogA-BYmfaUYISk1nvFwHvcYL2rskYJCBN_dO0Hau55ps5uxCecZRGHK2KVE0QFUIp4EHDUOGcXTOEF_FqM_vWvLDnrJCr8o_eUZn8=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224bf60000a70051c8_0%7C0a220b774bfa0000932c3671_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=E56ea0HvIMJJMw2mUun5THETKbmAH82UvgXrS90ou0st1zRYqVE3FWkJaUezJKtIedfacC6pNk_ssXI5WgsbcfVzFMSLpaxxHY-EsccMdaLmrPCqeD6-R3ZEKiRR0oaxKYia05xlNkaaGqTfeLtfQqTUiaDXlk8LwD9sAAv9LmNhNw4wGWYLiJNCRy93q1AF4eYUGKMDwQxC37ePe0IOe7kLRdwRGwZ8_4IcZKcOlbFo6m1HFJY3GevJithbxV16l3pfOzuhGiP4jwT6iMGX-W6JYfbCcpZ-B_yKDuhRkapIhm3KNhlv3jAVe8NmHjAP8gfBdcK2enTtjyQZmUJNrd63ZDYY2XE0Lftcn9GpuXDYghsEWvWX5E7328d69PsX23C5YJDUPFGA134DatJxKVUEdf4JeP_uB4ZJt06iw83N2Ddgt_M4bOuvC0YsTyP4Nn7Xuz3Fgb7IPwA9ypFhof1gx_J_KXaG_Q0yvbYuDoCyoOtbFH91C9VmX0jhWf3x7FJjmYy2f00gsLdBBXbtg84IpD8B24XkLPM-4K8JHkIDaOM3jMjTHvbUXtiyxUmfeAznejeoiYWf7RvEHD-ZnpCP4-BZqwkBDBuvQUe5a7CaN2Do0a9UhlF50RvsVK0ZKFLrwrlsItcvUSbefIh_TzHWP1ODxzuogJa05g7Wwz4hlytAeQEp4XiXw11KDDTZ8fAFzcZogA-BYmfaUYISk1nvFwHvcYL2rskYJCBN_dO0Hau55ps5uxCecZRGHK2KVE0QFUIp4EHDUOGcXTOEF_FqM_vWvLDnrJCr8o_eUZn8=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-03-30T21:15:00.000Z", "utc_arrival": "2023-03-30T19:15:00.000Z", "local_departure": "2023-03-30T17:45:00.000Z", "utc_departure": "2023-03-30T15:45:00.000Z"}, {"id": "0b770a224bf70000db6318b4_0|0a220b774bfa00006980c56e_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 918.989003, "distance": 1975.87, "duration": {"departure": 12600, "return": 11700, "total": 24300}, "price": 291466.9221, "conversion": {"EUR": 762.989393, "HUF": 291466.9221}, "fare": {"adults": 145733.46, "children": 145733.46, "infants": 145733.46}, "bags_price": {"1": 109.018, "2": 218.05}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 439, "hold_height": 149, "hold_length": 171, "hold_weight": 20, "hold_width": 119, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 2}, "airlines": ["W6"], "route": [{"id": "0b770a224bf70000db6318b4_0", "combination_id": "0b770a224bf70000db6318b4", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "HIREG", "fare_category": "M", "fare_classes": "H", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-03-31T19:45:00.000Z", "utc_arrival": "2023-03-31T17:45:00.000Z", "local_departure": "2023-03-31T16:15:00.000Z", "utc_departure": "2023-03-31T14:15:00.000Z"}, {"id": "0a220b774bfa00006980c56e_0", "combination_id": "0a220b774bfa00006980c56e", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "GFREG", "fare_category": "M", "fare_classes": "G", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-03T23:45:00.000Z", "utc_arrival": "2023-04-03T21:45:00.000Z", "local_departure": "2023-04-03T20:30:00.000Z", "utc_departure": "2023-04-03T18:30:00.000Z"}], "booking_token": "EgP8bAL0QrSSqgcwQQLzbwWdW9nt6bsuU_uovR_XNQA_J4Y0JyDqBR8Y8qMoj2ASqhY9Tldklnhz2Y6fkU2fwQpQfmEqxrBc0tKmmjkfVFbge5rouL_kDh2T_pX-XUp5ipiZfanfWAumXoHQb228j2BapSJrdJS29_6iaES4TfmxIzc9o3BYgg7GORsx5DVccAK70b6Wqnt59hKvYa90KwEOScxeAquG-QLxmWXbF25VRLC-b15v2KPTAaFD_5qmOVItgWEKLFiLemzZYHc9aL0gis3wkGFTioo3b8-_BkKedWcDWWcmt9ndci1Dhq0FVOmv0v4pxWO3yUPfyptO6iIFp-P-sNTXdTRckvjeyDfaM5rQz1CEilnuV5eLpJ0MCKAuWVVedpSLyVJ_T9c8Iw_aq3QgcsYxOgdIDGZOToW11M2DMm2w4_ufvNWhE3v5OnQrf8ntyFvDbU1jBhAS7dAaRyS_rCW46I2Q6--nGJ8MFR2D742PLa99Q_PUXcvn6wWwgaSQXS3PxsaOEqB7GOUWdz28s5ZzyqUTpXDt9T76l4Yqpu2meyJGzAVnOgY138Dn9WIkqLE96Dj1hU7zdOQgtVjLu8sSH6_vMbZbOr0d8ApRPJ1AHa0o76WRikHqfanPrX3V0Vl8wTtH9LierCdEW7E-50JSAheo5ZSiLpbBZG4COaNDlBAioruhtVdlHIDjiLEuUSJdt8j-FWbe1jOh18Lorto9rUBxWgod5xq-dVlOzDnDzQbcsUjNOVWkm2FjMBR76OS9G71UYAqia2H0gkMpYjueQdMzAfE9Vee0=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224bf70000db6318b4_0%7C0a220b774bfa00006980c56e_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EgP8bAL0QrSSqgcwQQLzbwWdW9nt6bsuU_uovR_XNQA_J4Y0JyDqBR8Y8qMoj2ASqhY9Tldklnhz2Y6fkU2fwQpQfmEqxrBc0tKmmjkfVFbge5rouL_kDh2T_pX-XUp5ipiZfanfWAumXoHQb228j2BapSJrdJS29_6iaES4TfmxIzc9o3BYgg7GORsx5DVccAK70b6Wqnt59hKvYa90KwEOScxeAquG-QLxmWXbF25VRLC-b15v2KPTAaFD_5qmOVItgWEKLFiLemzZYHc9aL0gis3wkGFTioo3b8-_BkKedWcDWWcmt9ndci1Dhq0FVOmv0v4pxWO3yUPfyptO6iIFp-P-sNTXdTRckvjeyDfaM5rQz1CEilnuV5eLpJ0MCKAuWVVedpSLyVJ_T9c8Iw_aq3QgcsYxOgdIDGZOToW11M2DMm2w4_ufvNWhE3v5OnQrf8ntyFvDbU1jBhAS7dAaRyS_rCW46I2Q6--nGJ8MFR2D742PLa99Q_PUXcvn6wWwgaSQXS3PxsaOEqB7GOUWdz28s5ZzyqUTpXDt9T76l4Yqpu2meyJGzAVnOgY138Dn9WIkqLE96Dj1hU7zdOQgtVjLu8sSH6_vMbZbOr0d8ApRPJ1AHa0o76WRikHqfanPrX3V0Vl8wTtH9LierCdEW7E-50JSAheo5ZSiLpbBZG4COaNDlBAioruhtVdlHIDjiLEuUSJdt8j-FWbe1jOh18Lorto9rUBxWgod5xq-dVlOzDnDzQbcsUjNOVWkm2FjMBR76OS9G71UYAqia2H0gkMpYjueQdMzAfE9Vee0=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-03-31T19:45:00.000Z", "utc_arrival": "2023-03-31T17:45:00.000Z", "local_departure": "2023-03-31T16:15:00.000Z", "utc_departure": "2023-03-31T14:15:00.000Z"}, {"id": "0b770a224beb000061734b61_0|0a220b774bef00006c5bf15f_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 923.19414, "distance": 1975.87, "duration": {"departure": 12000, "return": 11700, "total": 23700}, "price": 294091.9933, "conversion": {"EUR": 769.86119, "HUF": 294091.9933}, "fare": {"adults": 147046, "children": 147046, "infants": 147046}, "bags_price": {"1": 87.682, "2": 175.364}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 4}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224beb000061734b61_0", "combination_id": "0b770a224beb000061734b61", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "GHREG", "fare_category": "M", "fare_classes": "G", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-03-19T17:45:00.000Z", "utc_arrival": "2023-03-19T16:45:00.000Z", "local_departure": "2023-03-19T14:25:00.000Z", "utc_departure": "2023-03-19T13:25:00.000Z"}, {"id": "0a220b774bef00006c5bf15f_0", "combination_id": "0a220b774bef00006c5bf15f", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6709, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-03-23T09:55:00.000Z", "utc_arrival": "2023-03-23T08:55:00.000Z", "local_departure": "2023-03-23T06:40:00.000Z", "utc_departure": "2023-03-23T05:40:00.000Z"}], "booking_token": "EQxHT2T3lkW3dY-5XYwta0AFs6OdvjOmWMaY-6dvY8jY3k7CMy7PQOOVdJH9SNfHY49Pi75-ahfueWR8fKDbG-xar8abTkufhSMWDwCmpimtEvX6LwI4ZDNL33AZP4mr-HedzNx9_prXP5raQBNS7DZP_mAmC5y-hU9L2PwxdQyJX1u5Izqsdz92kbfGm-mNdYYOY0Kwfpt64BTvvQxEYXwY1IkexpBaSuqxu32GoXRB_3WI_H3qqPa36hwt1u2mLrlDOrhnzj9SdWPlcnzwVUnzuEid7z-cm9Tr1zlpsD5vlt1sPMAfQ8LvcPWhJ26ShlXqKCRY3HAPQ9auOLzrbiw6hgIp4v-Blppppy6rkMjsy2DyK59dmAL2cGRQgwzBV9L2f252i4niaaoIqPNLBdRWxqa8mY1zKtW4NrD-cGr7Mmfft_c9OMLf56YqxDdzXwddyoQBOOdsaHhfXtKUQQvBoBSG5UqjB8ER72u90ZQFQljtJRpNZmr4peq81tYhQsTVgYTwAE0gAFwHGIR9V490XEI0Hm972NErHvKXyb6MuzXks5QbJGo_o5I9eGPy0fvZb1b6NKOMaPU8QbRrHeu2-LTjwYJv9u73cZOgSGLnR4J7zZ824UFWUtwGZLMk9E95xjrBenzO0N2Aw4XO1RefbiYunlj_cjLzCkXaawPA9fHqp2cVfTQ_4xwB0fXMB2HrtKR9mGnOKFO6RiDxVkZMt58-Rbvz1xO1qmtJ_PHq_vnNmAJYstvOErGD3QKGWTQKYiAFg7kp5X9uw45x05w==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224beb000061734b61_0%7C0a220b774bef00006c5bf15f_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EQxHT2T3lkW3dY-5XYwta0AFs6OdvjOmWMaY-6dvY8jY3k7CMy7PQOOVdJH9SNfHY49Pi75-ahfueWR8fKDbG-xar8abTkufhSMWDwCmpimtEvX6LwI4ZDNL33AZP4mr-HedzNx9_prXP5raQBNS7DZP_mAmC5y-hU9L2PwxdQyJX1u5Izqsdz92kbfGm-mNdYYOY0Kwfpt64BTvvQxEYXwY1IkexpBaSuqxu32GoXRB_3WI_H3qqPa36hwt1u2mLrlDOrhnzj9SdWPlcnzwVUnzuEid7z-cm9Tr1zlpsD5vlt1sPMAfQ8LvcPWhJ26ShlXqKCRY3HAPQ9auOLzrbiw6hgIp4v-Blppppy6rkMjsy2DyK59dmAL2cGRQgwzBV9L2f252i4niaaoIqPNLBdRWxqa8mY1zKtW4NrD-cGr7Mmfft_c9OMLf56YqxDdzXwddyoQBOOdsaHhfXtKUQQvBoBSG5UqjB8ER72u90ZQFQljtJRpNZmr4peq81tYhQsTVgYTwAE0gAFwHGIR9V490XEI0Hm972NErHvKXyb6MuzXks5QbJGo_o5I9eGPy0fvZb1b6NKOMaPU8QbRrHeu2-LTjwYJv9u73cZOgSGLnR4J7zZ824UFWUtwGZLMk9E95xjrBenzO0N2Aw4XO1RefbiYunlj_cjLzCkXaawPA9fHqp2cVfTQ_4xwB0fXMB2HrtKR9mGnOKFO6RiDxVkZMt58-Rbvz1xO1qmtJ_PHq_vnNmAJYstvOErGD3QKGWTQKYiAFg7kp5X9uw45x05w==", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-03-19T17:45:00.000Z", "utc_arrival": "2023-03-19T16:45:00.000Z", "local_departure": "2023-03-19T14:25:00.000Z", "utc_departure": "2023-03-19T13:25:00.000Z"}, {"id": "0b770a224c120000d0b8a626_0|0a220b774c1500008ea7d1cf_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 932.398315, "distance": 1975.87, "duration": {"departure": 12600, "return": 11700, "total": 24300}, "price": 296589.3667, "conversion": {"EUR": 776.398705, "HUF": 296589.3667}, "fare": {"adults": 148294.68, "children": 148294.68, "infants": 148294.68}, "bags_price": {"1": 121.646, "2": 243.32}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 439, "hold_height": 149, "hold_length": 171, "hold_weight": 20, "hold_width": 119, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 2}, "airlines": ["W6"], "route": [{"id": "0b770a224c120000d0b8a626_0", "combination_id": "0b770a224c120000d0b8a626", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "HREG", "fare_category": "M", "fare_classes": "H", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-27T21:15:00.000Z", "utc_arrival": "2023-04-27T19:15:00.000Z", "local_departure": "2023-04-27T17:45:00.000Z", "utc_departure": "2023-04-27T15:45:00.000Z"}, {"id": "0a220b774c1500008ea7d1cf_0", "combination_id": "0a220b774c1500008ea7d1cf", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "GREG", "fare_category": "M", "fare_classes": "G", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-30T21:05:00.000Z", "utc_arrival": "2023-04-30T19:05:00.000Z", "local_departure": "2023-04-30T17:50:00.000Z", "utc_departure": "2023-04-30T15:50:00.000Z"}], "booking_token": "EDOK_6lkiXRZAN8G1FQTlHBdv4vYtZo6sn1lfuL_fk_qx8hz-GkMgJPDi-hHkaW_it_qYP41plN6g2Lt5h-rDYsP0Qhddt9kmEMs9boyIMth58ljSWlGA556Wr5V2A8UHSScvS1ECImkwv3fiBdt9qq8LOcbvarw1kV3U2FOETmg-8NPySQb12fA0pAShzbp7mrAH52XDYoVe0iHwc7Duw3vtwcNbdBACMZ-heezVR5urTGBkaMZESYx98zvwOFUVdpB4qDIZpn_nn9akiCEKhP1HCx08rr6ycdVOjQEhFZtgACynlEqb3cABTgs3ATvFTj-EWCSTf5mBoovEvKQcmyiBpLykNLE9F52cd6NY399oPHc5BEI-ms0NvSlrxhD22NZYIJqh1-lzNjc1JQY9KQW5g23fbHCnx2TbTi_OpaHxYhUi3bRorkJgkCj_tqWY3Wo_reVQXE99OOUWzpjK9bNiDr7VmJebJZ_cf_CQz8dbxeDxe1kBC6VC8d919wExTuihqezsL0u795IUPS5DKhrlN9aAQEbpLZBzYlvJjt4s-XUhG2kp-LQJoBDHSRWdXACD5lHNB7teqMZSER-wvR_T_yzByzPDz5FFktSXCgUcZ_GW02ampXxO4pLh5rDhPqeTgzq9BCZF--24EtHOzRSycvGQizC-E0xiGtwiZM29b2bNVB1yZrJspIYJcGkHlBvWKzj9r9MbfJarbqV_pEU5rY7rg7rR2qttoxeDSK60YRhFlmDXx5HVtEV7RsKUUcIEFVcD_uoGs7d63ftTOtpqbCRn2l-NVcFdeNhQQCg=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c120000d0b8a626_0%7C0a220b774c1500008ea7d1cf_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EDOK_6lkiXRZAN8G1FQTlHBdv4vYtZo6sn1lfuL_fk_qx8hz-GkMgJPDi-hHkaW_it_qYP41plN6g2Lt5h-rDYsP0Qhddt9kmEMs9boyIMth58ljSWlGA556Wr5V2A8UHSScvS1ECImkwv3fiBdt9qq8LOcbvarw1kV3U2FOETmg-8NPySQb12fA0pAShzbp7mrAH52XDYoVe0iHwc7Duw3vtwcNbdBACMZ-heezVR5urTGBkaMZESYx98zvwOFUVdpB4qDIZpn_nn9akiCEKhP1HCx08rr6ycdVOjQEhFZtgACynlEqb3cABTgs3ATvFTj-EWCSTf5mBoovEvKQcmyiBpLykNLE9F52cd6NY399oPHc5BEI-ms0NvSlrxhD22NZYIJqh1-lzNjc1JQY9KQW5g23fbHCnx2TbTi_OpaHxYhUi3bRorkJgkCj_tqWY3Wo_reVQXE99OOUWzpjK9bNiDr7VmJebJZ_cf_CQz8dbxeDxe1kBC6VC8d919wExTuihqezsL0u795IUPS5DKhrlN9aAQEbpLZBzYlvJjt4s-XUhG2kp-LQJoBDHSRWdXACD5lHNB7teqMZSER-wvR_T_yzByzPDz5FFktSXCgUcZ_GW02ampXxO4pLh5rDhPqeTgzq9BCZF--24EtHOzRSycvGQizC-E0xiGtwiZM29b2bNVB1yZrJspIYJcGkHlBvWKzj9r9MbfJarbqV_pEU5rY7rg7rR2qttoxeDSK60YRhFlmDXx5HVtEV7RsKUUcIEFVcD_uoGs7d63ftTOtpqbCRn2l-NVcFdeNhQQCg=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-04-27T21:15:00.000Z", "utc_arrival": "2023-04-27T19:15:00.000Z", "local_departure": "2023-04-27T17:45:00.000Z", "utc_departure": "2023-04-27T15:45:00.000Z"}, {"id": "0b770a224bfd00007895755b_0|0a220b774c01000036594325_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 932.563951, "distance": 1975.87, "duration": {"departure": 12600, "return": 11400, "total": 24000}, "price": 297161.9814, "conversion": {"EUR": 777.897671, "HUF": 297161.9814}, "fare": {"adults": 148580.99, "children": 148580.99, "infants": 148580.99}, "bags_price": {"1": 139.552, "2": 279.104}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 2}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224bfd00007895755b_0", "combination_id": "0b770a224bfd00007895755b", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "GFREG", "fare_category": "M", "fare_classes": "G", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-06T21:15:00.000Z", "utc_arrival": "2023-04-06T19:15:00.000Z", "local_departure": "2023-04-06T17:45:00.000Z", "utc_departure": "2023-04-06T15:45:00.000Z"}, {"id": "0a220b774c01000036594325_0", "combination_id": "0a220b774c01000036594325", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6713, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-10T10:15:00.000Z", "utc_arrival": "2023-04-10T08:15:00.000Z", "local_departure": "2023-04-10T07:05:00.000Z", "utc_departure": "2023-04-10T05:05:00.000Z"}], "booking_token": "Exz5XxAve-HOfA8bUf8l4k4JX1xJ-pDpGbj_UyzMFNGAXjxX-DzeDJvMTEgBk-FHFsygHIpF2pV-tfHvgW03rbQKLpxbR3zRoj9Jac-LJw6eTwBBbOgTI0ftDePI5tVI5nXJuswsh3xfiZawotiRyUWRihPI9uPX39sGIXfqSLZrgMk4L3u-nOMELIWQNYsanFV6N4CmNimQSVxI9Yyn90glI9_oq9G0AbuNH8ecMsRzdUCY9jTksiZxcGHhkLxMaiemVoZKYEbXV781amyRhtVwGvrhAq_Kl54ZtyuK6aq0Ijfk8I81nJl-I9l8HdyWAtqKFKAp9daFkIlSNaVlRmF8wP8RQHImIWFctHr0tuUEyW6xtT3g0G9jweEmMWE0Sog2mRCxDoLmbu9y8q7VO2of86Cr26cJxhpZs8GM5c2n2psPwnorgwsahAk4FoYbpUhco20rgH8tayHKoi5QdFBpg1yFkVcyHuUH85650NHk7JWlX0UtggBN3LSftScN0hLwVmPCB4vr-g7UG6ZhELwSsiep7IISD2ba_8gPCQhjtRzLTTGoh--D_G3TibCFgWUI5Q28HO3Bl2pqiDZO-gQkouicsTHasqofnBzAFHeAZ-4t5l5ymvtywfzaljAGet-XBQ3ztXSlyHJ_EDFxmbwsk47HpXxJKlrW6VclZDiKs8ppivs4CZ3PYuCnzpzLRc2OweLRtgu1TO_S0mu3wNZzqnnftyneSJWja1oGINlXAbbe4QCGdnyqZCfQEzeu_O1PKG9nBTDUcJ1ju1LYYQ3gekCrGH7paoyHvWSYtSX8=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224bfd00007895755b_0%7C0a220b774c01000036594325_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=Exz5XxAve-HOfA8bUf8l4k4JX1xJ-pDpGbj_UyzMFNGAXjxX-DzeDJvMTEgBk-FHFsygHIpF2pV-tfHvgW03rbQKLpxbR3zRoj9Jac-LJw6eTwBBbOgTI0ftDePI5tVI5nXJuswsh3xfiZawotiRyUWRihPI9uPX39sGIXfqSLZrgMk4L3u-nOMELIWQNYsanFV6N4CmNimQSVxI9Yyn90glI9_oq9G0AbuNH8ecMsRzdUCY9jTksiZxcGHhkLxMaiemVoZKYEbXV781amyRhtVwGvrhAq_Kl54ZtyuK6aq0Ijfk8I81nJl-I9l8HdyWAtqKFKAp9daFkIlSNaVlRmF8wP8RQHImIWFctHr0tuUEyW6xtT3g0G9jweEmMWE0Sog2mRCxDoLmbu9y8q7VO2of86Cr26cJxhpZs8GM5c2n2psPwnorgwsahAk4FoYbpUhco20rgH8tayHKoi5QdFBpg1yFkVcyHuUH85650NHk7JWlX0UtggBN3LSftScN0hLwVmPCB4vr-g7UG6ZhELwSsiep7IISD2ba_8gPCQhjtRzLTTGoh--D_G3TibCFgWUI5Q28HO3Bl2pqiDZO-gQkouicsTHasqofnBzAFHeAZ-4t5l5ymvtywfzaljAGet-XBQ3ztXSlyHJ_EDFxmbwsk47HpXxJKlrW6VclZDiKs8ppivs4CZ3PYuCnzpzLRc2OweLRtgu1TO_S0mu3wNZzqnnftyneSJWja1oGINlXAbbe4QCGdnyqZCfQEzeu_O1PKG9nBTDUcJ1ju1LYYQ3gekCrGH7paoyHvWSYtSX8=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-04-06T21:15:00.000Z", "utc_arrival": "2023-04-06T19:15:00.000Z", "local_departure": "2023-04-06T17:45:00.000Z", "utc_departure": "2023-04-06T15:45:00.000Z"}, {"id": "0b770a224bec0000c49ebb28_0|0a220b774bef00006f39da1f_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 934.941428, "distance": 1975.87, "duration": {"departure": 12000, "return": 11700, "total": 23700}, "price": 298579.5339, "conversion": {"EUR": 781.608478, "HUF": 298579.5339}, "fare": {"adults": 149289.77, "children": 156898.09, "infants": 156898.09}, "bags_price": {"1": 81.816, "2": 163.618}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 3}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224bec0000c49ebb28_0", "combination_id": "0b770a224bec0000c49ebb28", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "FR", "flight_no": 6712, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-03-20T23:50:00.000Z", "utc_arrival": "2023-03-20T22:50:00.000Z", "local_departure": "2023-03-20T20:30:00.000Z", "utc_departure": "2023-03-20T19:30:00.000Z"}, {"id": "0a220b774bef00006f39da1f_0", "combination_id": "0a220b774bef00006f39da1f", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "IREG", "fare_category": "M", "fare_classes": "I", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-03-24T00:05:00.000Z", "utc_arrival": "2023-03-23T23:05:00.000Z", "local_departure": "2023-03-23T20:50:00.000Z", "utc_departure": "2023-03-23T19:50:00.000Z"}], "booking_token": "EFs9ZAQA-Gi-ROUzmsTOjpqFa1AP6X64iBuSSTkiN1zP8ZejlPzNMZed-pf5HcLMBtGg9ZkcGwiNopU1LoBg8PHj8vwlY1-G03bgZaNLzull1SsAozsIgkvj03FBNGS0cCU7cvaGBU0oqz4F6jSiz-W90ItuVmga3PYCc1rQVgL3cR2Pfhi4VZopW9XVgsxS_9bPz0C9_qm2PRDpvq_qGEtxRzO2qc4Mzb63w5hs_l1csafVhXqV--WgPFPjQA5JV3YsThDb-6tHnj1W6i2cnjySoxeEnoOO6SwZep12rXAtsDFqmHkKadW6NISJsjUPxrYGEF9Q7Xj1AVCNHAKgpsHQak1q64vmJCJAhQtHfjiRvUhE6BI2_W0cjm8z6FzppQoHUQM07XxnthPUtpFi1BLxnVDK9rBPT2l4-PO1-8rny2XgbzQBGyso5CiNKlupxDLBRrUXbCllK8m0GxMo7wCQ67TlCcHkGN5B34huHwoGoTTb9SPeUSluUGqsGcGZUxclntFmAUX-eAnIKMPcb4lXeFA_aLZgjeYpIVMFdOnRsEVgMokle4uFbo0nmHTDbBEQH8ojzpVVLZELftwWlwhiy-zbjpYqwXCkSgGjOr51eSA29xl6hON5WDUU4Ew7T87eXVtRDMvb7JV5fOmZ3TN3NOKBqeQnZeDbljnlY8Pa7RrdqbWJWZL8zgEmgNFGiGXdxv8LuU9HzWqEYvXeGMGmPB4iPFDzt_yl5gkftw1EqoTG-gpSzc3q4zp4SwffFBhJ3vLBtBfkh3Qf7OytKu3KYBnIFN42Y_lBmwJJxbBA=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224bec0000c49ebb28_0%7C0a220b774bef00006f39da1f_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EFs9ZAQA-Gi-ROUzmsTOjpqFa1AP6X64iBuSSTkiN1zP8ZejlPzNMZed-pf5HcLMBtGg9ZkcGwiNopU1LoBg8PHj8vwlY1-G03bgZaNLzull1SsAozsIgkvj03FBNGS0cCU7cvaGBU0oqz4F6jSiz-W90ItuVmga3PYCc1rQVgL3cR2Pfhi4VZopW9XVgsxS_9bPz0C9_qm2PRDpvq_qGEtxRzO2qc4Mzb63w5hs_l1csafVhXqV--WgPFPjQA5JV3YsThDb-6tHnj1W6i2cnjySoxeEnoOO6SwZep12rXAtsDFqmHkKadW6NISJsjUPxrYGEF9Q7Xj1AVCNHAKgpsHQak1q64vmJCJAhQtHfjiRvUhE6BI2_W0cjm8z6FzppQoHUQM07XxnthPUtpFi1BLxnVDK9rBPT2l4-PO1-8rny2XgbzQBGyso5CiNKlupxDLBRrUXbCllK8m0GxMo7wCQ67TlCcHkGN5B34huHwoGoTTb9SPeUSluUGqsGcGZUxclntFmAUX-eAnIKMPcb4lXeFA_aLZgjeYpIVMFdOnRsEVgMokle4uFbo0nmHTDbBEQH8ojzpVVLZELftwWlwhiy-zbjpYqwXCkSgGjOr51eSA29xl6hON5WDUU4Ew7T87eXVtRDMvb7JV5fOmZ3TN3NOKBqeQnZeDbljnlY8Pa7RrdqbWJWZL8zgEmgNFGiGXdxv8LuU9HzWqEYvXeGMGmPB4iPFDzt_yl5gkftw1EqoTG-gpSzc3q4zp4SwffFBhJ3vLBtBfkh3Qf7OytKu3KYBnIFN42Y_lBmwJJxbBA=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-03-20T23:50:00.000Z", "utc_arrival": "2023-03-20T22:50:00.000Z", "local_departure": "2023-03-20T20:30:00.000Z", "utc_departure": "2023-03-20T19:30:00.000Z"}, {"id": "0b770a224c224c2531320fa7_0|0b770a224c224c2531320fa7_1", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 3, "quality": 945.987796, "distance": 1975.87, "duration": {"departure": 11700, "return": 11400, "total": 23100}, "price": 303818, "conversion": {"EUR": 795.321506, "HUF": 303818}, "fare": {"adults": 151909, "children": 151909, "infants": 151909}, "bags_price": {"1": 78.4, "2": 176.4}, "baglimit": {"hand_height": 40, "hand_length": 56, "hand_weight": 10, "hand_width": 25, "hold_dimensions_sum": 158, "hold_height": 52, "hold_length": 78, "hold_weight": 23, "hold_width": 28, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 3, "personal_item_width": 15}, "availability": {"seats": 2}, "airlines": ["IB"], "route": [{"id": "0b770a224c224c2531320fa7_0", "combination_id": "0b770a224c224c2531320fa7", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "IB", "flight_no": 3279, "operating_carrier": "IB", "operating_flight_no": "3279", "fare_basis": "SDNNANB4", "fare_category": "M", "fare_classes": "S", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-13T18:50:00.000Z", "utc_arrival": "2023-05-13T16:50:00.000Z", "local_departure": "2023-05-13T15:35:00.000Z", "utc_departure": "2023-05-13T13:35:00.000Z"}, {"id": "0b770a224c224c2531320fa7_1", "combination_id": "0b770a224c224c2531320fa7", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "IB", "flight_no": 3278, "operating_carrier": "IB", "operating_flight_no": "3278", "fare_basis": "VDNNANB4", "fare_category": "M", "fare_classes": "V", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-05-16T14:55:00.000Z", "utc_arrival": "2023-05-16T12:55:00.000Z", "local_departure": "2023-05-16T11:45:00.000Z", "utc_departure": "2023-05-16T09:45:00.000Z"}], "booking_token": "EHlaPQl_fHxFAM762rpap87FdQnuP79MG2i-WiPct-53LSkWHryVd_X5zgnSN38sU8TqZiGcFr08N1WKLS3o-bxgoYTkQJqgxRoEGdBcw7oyYKy9F3GEMriB-2d56N8JG0xCvWxAdk2XxSDkd6dD51bdwNVC4h5Qp3VVZJOuAk3L35Z3J7i1TLX45xOyIFq914xiToKHqWSY2Aipaj7men_bkLvo_u9ZMxDHFjdKIoVwKLmVUnS-NkiX3IJxexhuWtrLrf3kd0a0Y_GCgxaycJgyZ9cYoWkyzgijKDS6Bw6E27xZ1SHuQSSj78ThOP__3I-5DwiYCy0zleFUKIy60r2xxbAPRKvwBtubbFLWo6szQu52u9a1T-2Us7JGrMTUVyMc_L4MX2bS8mdSVPnCoWT7cNlw4b5WdsYQJxkXfh7Zxru0xLBWSkA4EF6kBVw8E7QeocofX-M5lEcrP4vp_xiXgls_dgfhGyNHdeh8x-1Q9j9z5Ul7zt_bUzbTmLqYJ-kMFwBSVHaj07nxouQ_ufbNqGP9MKhcaWdWt2YffNTG0wAb47SNc8sG8bFNclZXOi5OFu9tnEDCoX0CiCDS93aWQa3LGBdGJmL2J4BwfHdMgKOVTjLW43H7HTXKnSnpUiIGlGQdiC_AFGhnOQvOGtWpoVljC2rB8Qe-_dixGNlIr3S1NvJ-LqlBxeMQ0tgQUs072eJHmXvgl0PIzoKUn3Q==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c224c2531320fa7_0%7C0b770a224c224c2531320fa7_1&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EHlaPQl_fHxFAM762rpap87FdQnuP79MG2i-WiPct-53LSkWHryVd_X5zgnSN38sU8TqZiGcFr08N1WKLS3o-bxgoYTkQJqgxRoEGdBcw7oyYKy9F3GEMriB-2d56N8JG0xCvWxAdk2XxSDkd6dD51bdwNVC4h5Qp3VVZJOuAk3L35Z3J7i1TLX45xOyIFq914xiToKHqWSY2Aipaj7men_bkLvo_u9ZMxDHFjdKIoVwKLmVUnS-NkiX3IJxexhuWtrLrf3kd0a0Y_GCgxaycJgyZ9cYoWkyzgijKDS6Bw6E27xZ1SHuQSSj78ThOP__3I-5DwiYCy0zleFUKIy60r2xxbAPRKvwBtubbFLWo6szQu52u9a1T-2Us7JGrMTUVyMc_L4MX2bS8mdSVPnCoWT7cNlw4b5WdsYQJxkXfh7Zxru0xLBWSkA4EF6kBVw8E7QeocofX-M5lEcrP4vp_xiXgls_dgfhGyNHdeh8x-1Q9j9z5Ul7zt_bUzbTmLqYJ-kMFwBSVHaj07nxouQ_ufbNqGP9MKhcaWdWt2YffNTG0wAb47SNc8sG8bFNclZXOi5OFu9tnEDCoX0CiCDS93aWQa3LGBdGJmL2J4BwfHdMgKOVTjLW43H7HTXKnSnpUiIGlGQdiC_AFGhnOQvOGtWpoVljC2rB8Qe-_dixGNlIr3S1NvJ-LqlBxeMQ0tgQUs072eJHmXvgl0PIzoKUn3Q==", "facilitated_booking_available": true, "pnr_count": 1, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-05-13T18:50:00.000Z", "utc_arrival": "2023-05-13T16:50:00.000Z", "local_departure": "2023-05-13T15:35:00.000Z", "utc_departure": "2023-05-13T13:35:00.000Z"}, {"id": "0b770a224be90000545afd59_0|0a220b774bed0000ac01fd86_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 948.918801, "distance": 1975.87, "duration": {"departure": 12000, "return": 11700, "total": 23700}, "price": 303918.9815, "conversion": {"EUR": 795.585851, "HUF": 303918.9815}, "fare": {"adults": 151959.49, "children": 151959.49, "infants": 151959.49}, "bags_price": {"1": 95.704, "2": 191.422}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 20, "hold_dimensions_sum": 319, "hold_height": 119, "hold_length": 119, "hold_weight": 20, "hold_width": 81, "personal_item_height": 25, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 3}, "airlines": ["FR", "W6"], "route": [{"id": "0b770a224be90000545afd59_0", "combination_id": "0b770a224be90000545afd59", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "HIREG", "fare_category": "M", "fare_classes": "H", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-03-17T20:10:00.000Z", "utc_arrival": "2023-03-17T19:10:00.000Z", "local_departure": "2023-03-17T16:50:00.000Z", "utc_departure": "2023-03-17T15:50:00.000Z"}, {"id": "0a220b774bed0000ac01fd86_0", "combination_id": "0a220b774bed0000ac01fd86", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "FR", "flight_no": 6709, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "", "fare_category": "M", "fare_classes": "", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-03-21T16:05:00.000Z", "utc_arrival": "2023-03-21T15:05:00.000Z", "local_departure": "2023-03-21T12:50:00.000Z", "utc_departure": "2023-03-21T11:50:00.000Z"}], "booking_token": "EJB68Iu02e4UvBV7QJO2g_bgr3U6mY3tcr8JqjDC_nCzqb3ILy-wdts9dZ51B0ZQ00HlUrwSZjj-u4gg1TPiIgoWxAiWBeKjGzlN1YDtOTEL_cb7Fxx6ki3N66o6zBfhSmO_JuAem40Nk5xNf952Wxh8PJKWd1VB9TWW3wsU7HVSDgD6ok-sksl5ckMhb2uSDYttQ41qx2UIlFTWDjwIiWDrpqgRCOdS_dBwM0RFa7oxJTkmY5gpZthkTt25BFopUq4rxJFTkDE8ly0tvTVdbigLsZfC7Y59MV8EfkJVIIN7CmXarhdwTA2J16uHiF9FQbeZ7-and2uO4Eeny-WqyA2JndxzSWh42vv_mGg2jKPE7orpmGsuwyFkpMS1b6lc0IN6mRqLi5kd042jzoFrdABPFvp7BKpiM0B2mkyryuoDADolVdxLOMZjzz1JG3PoMb1YZdolWNpVD5pTMqnGp4pcF9wgD9pbUUuuxgtmUdPYOqWvaF3hEo48gCrwf0DSveKYLl92LJGor_vM-S8eTd2m7320Qq2elHJIV28SlQlVRpf0vdNqYskuZVJN1CDpzjPr_JQ4Os2aT1NFP0tMniAh2D5kGkm4AymWeZdif_yc_wI_ab1RMJlb--yfR1YMMzjQk5OTdveE5yWnY45g25U9YqiTiUI8RDf2be37wU05IHFtbN_W9cMclf2fAFVRoeP75XkW8inQmY92syPh7Dxov0BsWs89_WEVCvrM6bVT0kmjmFDLJngBxAWPXtGj5WIo3sk5x4PG3kXUK9Fv33_cNq2aeZjVBHPJB0Y75bW0=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224be90000545afd59_0%7C0a220b774bed0000ac01fd86_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EJB68Iu02e4UvBV7QJO2g_bgr3U6mY3tcr8JqjDC_nCzqb3ILy-wdts9dZ51B0ZQ00HlUrwSZjj-u4gg1TPiIgoWxAiWBeKjGzlN1YDtOTEL_cb7Fxx6ki3N66o6zBfhSmO_JuAem40Nk5xNf952Wxh8PJKWd1VB9TWW3wsU7HVSDgD6ok-sksl5ckMhb2uSDYttQ41qx2UIlFTWDjwIiWDrpqgRCOdS_dBwM0RFa7oxJTkmY5gpZthkTt25BFopUq4rxJFTkDE8ly0tvTVdbigLsZfC7Y59MV8EfkJVIIN7CmXarhdwTA2J16uHiF9FQbeZ7-and2uO4Eeny-WqyA2JndxzSWh42vv_mGg2jKPE7orpmGsuwyFkpMS1b6lc0IN6mRqLi5kd042jzoFrdABPFvp7BKpiM0B2mkyryuoDADolVdxLOMZjzz1JG3PoMb1YZdolWNpVD5pTMqnGp4pcF9wgD9pbUUuuxgtmUdPYOqWvaF3hEo48gCrwf0DSveKYLl92LJGor_vM-S8eTd2m7320Qq2elHJIV28SlQlVRpf0vdNqYskuZVJN1CDpzjPr_JQ4Os2aT1NFP0tMniAh2D5kGkm4AymWeZdif_yc_wI_ab1RMJlb--yfR1YMMzjQk5OTdveE5yWnY45g25U9YqiTiUI8RDf2be37wU05IHFtbN_W9cMclf2fAFVRoeP75XkW8inQmY92syPh7Dxov0BsWs89_WEVCvrM6bVT0kmjmFDLJngBxAWPXtGj5WIo3sk5x4PG3kXUK9Fv33_cNq2aeZjVBHPJB0Y75bW0=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-03-17T20:10:00.000Z", "utc_arrival": "2023-03-17T19:10:00.000Z", "local_departure": "2023-03-17T16:50:00.000Z", "utc_departure": "2023-03-17T15:50:00.000Z"}, {"id": "0b770a224c364c3ac8c12d58_0|0b770a224c364c3ac8c12d58_1", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 947.924936, "distance": 1975.87, "duration": {"departure": 11700, "return": 11400, "total": 23100}, "price": 304558.0001, "conversion": {"EUR": 797.258646, "HUF": 304558.0001}, "fare": {"adults": 152279, "children": 152279, "infants": 152279}, "bags_price": {"1": 78.4, "2": 176.4}, "baglimit": {"hand_height": 40, "hand_length": 56, "hand_weight": 10, "hand_width": 25, "hold_dimensions_sum": 158, "hold_height": 52, "hold_length": 78, "hold_weight": 23, "hold_width": 28, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 3, "personal_item_width": 15}, "availability": {"seats": 9}, "airlines": ["IB"], "route": [{"id": "0b770a224c364c3ac8c12d58_0", "combination_id": "0b770a224c364c3ac8c12d58", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "IB", "flight_no": 3279, "operating_carrier": "IB", "operating_flight_no": "3279", "fare_basis": "SDNNANB4", "fare_category": "M", "fare_classes": "S", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-02T18:50:00.000Z", "utc_arrival": "2023-06-02T16:50:00.000Z", "local_departure": "2023-06-02T15:35:00.000Z", "utc_departure": "2023-06-02T13:35:00.000Z"}, {"id": "0b770a224c364c3ac8c12d58_1", "combination_id": "0b770a224c364c3ac8c12d58", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "IB", "flight_no": 3278, "operating_carrier": "IB", "operating_flight_no": "3278", "fare_basis": "VDNNANB4", "fare_category": "M", "fare_classes": "V", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-06-06T14:55:00.000Z", "utc_arrival": "2023-06-06T12:55:00.000Z", "local_departure": "2023-06-06T11:45:00.000Z", "utc_departure": "2023-06-06T09:45:00.000Z"}], "booking_token": "Eb7uadg3VBHTGJg5saf9DANYFkNTWYoFLH1t__QLAF6ED8zRb2btTwB00P_-mfCLOlW02p5ryc4TSrjTveqhVcl9Gy3bcBNApzgLDTvoyrmdjfEkEbRa3dk0lojDhIdpOSr4zHGgFJ1IokOtS9u5rFIwPINzssJr0OTU49RV1TfxPrlOZVWYpH1m24mGmREoY7lZEo9187qAIX5OjRPn5JXiP-O3PbBxmKYN5KWsHHv-ytSgmFRdWpwAGE5_wArGy2SWlSYXc6NCpkmx9gjviWsb7A_g9B1v_kObOTpEiejp_VGd5_-orbAR--EvTDw9ZGgZ6PbLHsrt3w7cAWYflPK36Hs09lIuwUSWzGaIZntUVJJTzb9qBgQ53CTWKiZ77O8Hg358O4l1gqxqKPfYozMrBeMStlVCG6aJiT7nOABR6Vj6IdlXkbWl8lHl0PGlxgdnIce7JJmQtmOhro-ScfyDzPk9kXXo51I-VUyExJ_bC-bmPt8nfHZgW0XMXFqkfuhqzuCwz0U8XhvyMmUd1CM5W2X_mVqEL0osftaJpDzq2fCQLcjaq9syr_FIB8NBzFZvsiaG778r2zmPIwHoG_UBYWsojgwk4g--EmhjhngnN6w_c7kDXcBCpa7WsFI83izOnnU7JHczbrD85Jlbf0ZH93MmZ859ThsK-PkmKHDxqgjeW-jfAbQPncaNjxnKbsYVktrWg4UItvtnxCGlSHpHINdeAcRbOnCx2n9jWhq_ZQnPbAgQGL0UJvWSd-k2MZeRoLUzLSY2K78s0FJta6A==", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224c364c3ac8c12d58_0%7C0b770a224c364c3ac8c12d58_1&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=Eb7uadg3VBHTGJg5saf9DANYFkNTWYoFLH1t__QLAF6ED8zRb2btTwB00P_-mfCLOlW02p5ryc4TSrjTveqhVcl9Gy3bcBNApzgLDTvoyrmdjfEkEbRa3dk0lojDhIdpOSr4zHGgFJ1IokOtS9u5rFIwPINzssJr0OTU49RV1TfxPrlOZVWYpH1m24mGmREoY7lZEo9187qAIX5OjRPn5JXiP-O3PbBxmKYN5KWsHHv-ytSgmFRdWpwAGE5_wArGy2SWlSYXc6NCpkmx9gjviWsb7A_g9B1v_kObOTpEiejp_VGd5_-orbAR--EvTDw9ZGgZ6PbLHsrt3w7cAWYflPK36Hs09lIuwUSWzGaIZntUVJJTzb9qBgQ53CTWKiZ77O8Hg358O4l1gqxqKPfYozMrBeMStlVCG6aJiT7nOABR6Vj6IdlXkbWl8lHl0PGlxgdnIce7JJmQtmOhro-ScfyDzPk9kXXo51I-VUyExJ_bC-bmPt8nfHZgW0XMXFqkfuhqzuCwz0U8XhvyMmUd1CM5W2X_mVqEL0osftaJpDzq2fCQLcjaq9syr_FIB8NBzFZvsiaG778r2zmPIwHoG_UBYWsojgwk4g--EmhjhngnN6w_c7kDXcBCpa7WsFI83izOnnU7JHczbrD85Jlbf0ZH93MmZ859ThsK-PkmKHDxqgjeW-jfAbQPncaNjxnKbsYVktrWg4UItvtnxCGlSHpHINdeAcRbOnCx2n9jWhq_ZQnPbAgQGL0UJvWSd-k2MZeRoLUzLSY2K78s0FJta6A==", "facilitated_booking_available": true, "pnr_count": 1, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-06-02T18:50:00.000Z", "utc_arrival": "2023-06-02T16:50:00.000Z", "local_departure": "2023-06-02T15:35:00.000Z", "utc_departure": "2023-06-02T13:35:00.000Z"}, {"id": "0b770a224be8000084d26d37_0|0a220b774bec00004eadb5fe_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 953.261019, "distance": 1975.87, "duration": {"departure": 12000, "return": 11700, "total": 23700}, "price": 305577.7371, "conversion": {"EUR": 799.928069, "HUF": 305577.7371}, "fare": {"adults": 152788.87, "children": 152788.87, "infants": 152788.87}, "bags_price": {"1": 95.214, "2": 190.442}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 439, "hold_height": 149, "hold_length": 171, "hold_weight": 20, "hold_width": 119, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 2}, "airlines": ["W6"], "route": [{"id": "0b770a224be8000084d26d37_0", "combination_id": "0b770a224be8000084d26d37", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "JKREG", "fare_category": "M", "fare_classes": "J", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-03-16T19:40:00.000Z", "utc_arrival": "2023-03-16T18:40:00.000Z", "local_departure": "2023-03-16T16:20:00.000Z", "utc_departure": "2023-03-16T15:20:00.000Z"}, {"id": "0a220b774bec00004eadb5fe_0", "combination_id": "0a220b774bec00004eadb5fe", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "EDREG", "fare_category": "M", "fare_classes": "E", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-03-20T12:20:00.000Z", "utc_arrival": "2023-03-20T11:20:00.000Z", "local_departure": "2023-03-20T09:05:00.000Z", "utc_departure": "2023-03-20T08:05:00.000Z"}], "booking_token": "E270HwuZDsQFm94zVlUrObnZqwIYuqet7TOVP1B-rxC6bx3pxe2aOtNuAY3Aroa3pDr60wdYdmBSw0H6uat_P5Diz0x_gyiZpaj_WDfxbJ-Zjqrkj15uFjvdmB_UDBR3nFYiUeT13r0CvnOCfufzDBJXcrucpm-JFE8yF1AiPeWEr-qEZxphWqbuOPhvxnlLB9_5NhqDwKWLOlhj02AVEVl5Of4ZFDswYjWcizsJlWe2Thrg_SasVWCboaUSxlyyPpCPCkKMvU1YoKPmIT2K4Eid_2OPVSTuagNzT80Ac1FwA2d1a5xf4-lXqpWzKq8Ed3hgIzKWGNOeLXTPqi7_V_JQggxx1Av_sRa0R_d4AiV7G6Wn3YnePZtMK7yWXSOeuln0IACbHp-1ej1vKSZ0L8AEwDaE-eE4R4KCh0fiPg6kQDl6dBswCQ0ZutOAtl9TRlVLagGnkmenGcx6Z2ktJ4feoF6-n00WUy_5_TE1pjQV9HYQTN1vPV7J1ONb3ySbqjB2WGl1TEJoP4ebYcwWwMUaYmcAroR0K6Hwpmlk6M8yFcAMvM-yqTnRH7SeLAGHu1sPGG-zcTv6nd5r4oz8UQUmN7lRIWoXXjk2g9CTc301oszxOchxvhLuZBOmkrelLu3-Cj10QcsVvzl1mVj3OMIrVK-pdTgf3A9KMONoY6ZQN3XChpa1rLrgupj_Yk3WRAGYNuG5Un3MQ1JjAdoX5AUoVtQplAlHiaDDSEfZ671wiGTwI0Q6aE3Jl3qP0DwaZYfuU7iU_snzEfevGIBk-YUhPG-rDP-14olimSOMCfI3vsNtVvtXRd1UaxtBaWmOn", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224be8000084d26d37_0%7C0a220b774bec00004eadb5fe_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=E270HwuZDsQFm94zVlUrObnZqwIYuqet7TOVP1B-rxC6bx3pxe2aOtNuAY3Aroa3pDr60wdYdmBSw0H6uat_P5Diz0x_gyiZpaj_WDfxbJ-Zjqrkj15uFjvdmB_UDBR3nFYiUeT13r0CvnOCfufzDBJXcrucpm-JFE8yF1AiPeWEr-qEZxphWqbuOPhvxnlLB9_5NhqDwKWLOlhj02AVEVl5Of4ZFDswYjWcizsJlWe2Thrg_SasVWCboaUSxlyyPpCPCkKMvU1YoKPmIT2K4Eid_2OPVSTuagNzT80Ac1FwA2d1a5xf4-lXqpWzKq8Ed3hgIzKWGNOeLXTPqi7_V_JQggxx1Av_sRa0R_d4AiV7G6Wn3YnePZtMK7yWXSOeuln0IACbHp-1ej1vKSZ0L8AEwDaE-eE4R4KCh0fiPg6kQDl6dBswCQ0ZutOAtl9TRlVLagGnkmenGcx6Z2ktJ4feoF6-n00WUy_5_TE1pjQV9HYQTN1vPV7J1ONb3ySbqjB2WGl1TEJoP4ebYcwWwMUaYmcAroR0K6Hwpmlk6M8yFcAMvM-yqTnRH7SeLAGHu1sPGG-zcTv6nd5r4oz8UQUmN7lRIWoXXjk2g9CTc301oszxOchxvhLuZBOmkrelLu3-Cj10QcsVvzl1mVj3OMIrVK-pdTgf3A9KMONoY6ZQN3XChpa1rLrgupj_Yk3WRAGYNuG5Un3MQ1JjAdoX5AUoVtQplAlHiaDDSEfZ671wiGTwI0Q6aE3Jl3qP0DwaZYfuU7iU_snzEfevGIBk-YUhPG-rDP-14olimSOMCfI3vsNtVvtXRd1UaxtBaWmOn", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-03-16T19:40:00.000Z", "utc_arrival": "2023-03-16T18:40:00.000Z", "local_departure": "2023-03-16T16:20:00.000Z", "utc_departure": "2023-03-16T15:20:00.000Z"}, {"id": "0b770a224bfd00007895755b_0|0a220b774c010000ccf5b03a_0", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "countryFrom": {"code": "HU", "name": "Hungary"}, "countryTo": {"code": "ES", "name": "Spain"}, "nightsInDest": 4, "quality": 959.80439, "distance": 1975.87, "duration": {"departure": 12600, "return": 11700, "total": 24300}, "price": 307058.666, "conversion": {"EUR": 803.80478, "HUF": 307058.666}, "fare": {"adults": 153529.33, "children": 153529.33, "infants": 153529.33}, "bags_price": {"1": 141.974, "2": 283.948}, "baglimit": {"hand_height": 40, "hand_length": 55, "hand_weight": 10, "hand_width": 23, "hold_dimensions_sum": 439, "hold_height": 149, "hold_length": 171, "hold_weight": 20, "hold_width": 119, "personal_item_height": 30, "personal_item_length": 40, "personal_item_weight": 10, "personal_item_width": 20}, "availability": {"seats": 2}, "airlines": ["W6"], "route": [{"id": "0b770a224bfd00007895755b_0", "combination_id": "0b770a224bfd00007895755b", "flyFrom": "BUD", "flyTo": "MAD", "cityFrom": "Budapest", "cityCodeFrom": "BUD", "cityTo": "Madrid", "cityCodeTo": "MAD", "airline": "W6", "flight_no": 2371, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "GFREG", "fare_category": "M", "fare_classes": "G", "fare_family": "", "return": 0, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-06T21:15:00.000Z", "utc_arrival": "2023-04-06T19:15:00.000Z", "local_departure": "2023-04-06T17:45:00.000Z", "utc_departure": "2023-04-06T15:45:00.000Z"}, {"id": "0a220b774c010000ccf5b03a_0", "combination_id": "0a220b774c010000ccf5b03a", "flyFrom": "MAD", "flyTo": "BUD", "cityFrom": "Madrid", "cityCodeFrom": "MAD", "cityTo": "Budapest", "cityCodeTo": "BUD", "airline": "W6", "flight_no": 2372, "operating_carrier": "", "operating_flight_no": "", "fare_basis": "HIREG", "fare_category": "M", "fare_classes": "H", "fare_family": "", "return": 1, "bags_recheck_required": false, "vi_connection": false, "guarantee": false, "equipment": null, "vehicle_type": "aircraft", "local_arrival": "2023-04-10T23:45:00.000Z", "utc_arrival": "2023-04-10T21:45:00.000Z", "local_departure": "2023-04-10T20:30:00.000Z", "utc_departure": "2023-04-10T18:30:00.000Z"}], "booking_token": "EN0c73XPLFk8eboHIvcWgnSZOPHDp6g4OluK7eamR0oqBVu-qNCBYVDt2IbsjsTo4v69Tx8_Gmizs4VmgP_j0E3nEaqSvEydoWnan6--dbvwOmrey66zIjdrpAPHFOx3dxZpPNCiem8pZRk04PImRFwJ2a2Rw3JGpa7P5TCNGDF_Jm089Un9nvBvnCS3KJHoJ0LIduNXtkAoOzvkY5oKHfJ8_sOc1B1EXixD2MnZns2Lpc8hrKfAbvzWY1cQIGDu9gbDBD0ITviU8mR4Sqv0LvrCm4r55DYRIe3BC-DoRHwKH8L_jIdkbdp3jWcqv7BCfwLtuUOTE4f9by4AQzxNXU7i44aeYDxlqUOVslFoOjz-TP95vKtgkm1EZR0S8FsjT74bKhRAf9xwTDGdiJ7KoJFwb96CXakE6ZrTplyOXhT_FbDzZIrsEoCIIcAuXRxlVuybG3EOOsau61h7WcsKLJZtAW7on-5c7Vv5ajNOxDDwMQTHHq4xLzs_BZAGFh2r46_wBmRCCFnfBJd1E9hdSwBHesqf4B11E-dcV1X5J2ojld-RW2BY12mDaEPLWyb4UXByMFt8-kCV2N6wE6Qc_1sSq9kR1hd6rJIsL6_a1pbxExUBMXY1rWGFL6pZJGKopEsYaPK8DEi68uL_ZlokD76z6UIdSMifXNAOap_3flXd-Ls15ehF9r5neie-HuGfO4WK_Yr11jg8zOQUz-ypu-pXaRb0s5Q4h70GnN6wdjjzvSHEMMEcZnDYzu-5G81U_bHa491UHb9MZultc4NR9-VlnpuAdwdNxE_nS6hz6zLk=", "deep_link": "https://www.kiwi.com/deep?affilid=kulig1985kuligflight&currency=HUF&flightsId=0b770a224bfd00007895755b_0%7C0a220b774c010000ccf5b03a_0&from=BUD&lang=en&passengers=2&searchBags=1.0_1.0&to=MAD&booking_token=EN0c73XPLFk8eboHIvcWgnSZOPHDp6g4OluK7eamR0oqBVu-qNCBYVDt2IbsjsTo4v69Tx8_Gmizs4VmgP_j0E3nEaqSvEydoWnan6--dbvwOmrey66zIjdrpAPHFOx3dxZpPNCiem8pZRk04PImRFwJ2a2Rw3JGpa7P5TCNGDF_Jm089Un9nvBvnCS3KJHoJ0LIduNXtkAoOzvkY5oKHfJ8_sOc1B1EXixD2MnZns2Lpc8hrKfAbvzWY1cQIGDu9gbDBD0ITviU8mR4Sqv0LvrCm4r55DYRIe3BC-DoRHwKH8L_jIdkbdp3jWcqv7BCfwLtuUOTE4f9by4AQzxNXU7i44aeYDxlqUOVslFoOjz-TP95vKtgkm1EZR0S8FsjT74bKhRAf9xwTDGdiJ7KoJFwb96CXakE6ZrTplyOXhT_FbDzZIrsEoCIIcAuXRxlVuybG3EOOsau61h7WcsKLJZtAW7on-5c7Vv5ajNOxDDwMQTHHq4xLzs_BZAGFh2r46_wBmRCCFnfBJd1E9hdSwBHesqf4B11E-dcV1X5J2ojld-RW2BY12mDaEPLWyb4UXByMFt8-kCV2N6wE6Qc_1sSq9kR1hd6rJIsL6_a1pbxExUBMXY1rWGFL6pZJGKopEsYaPK8DEi68uL_ZlokD76z6UIdSMifXNAOap_3flXd-Ls15ehF9r5neie-HuGfO4WK_Yr11jg8zOQUz-ypu-pXaRb0s5Q4h70GnN6wdjjzvSHEMMEcZnDYzu-5G81U_bHa491UHb9MZultc4NR9-VlnpuAdwdNxE_nS6hz6zLk=", "facilitated_booking_available": false, "pnr_count": 2, "has_airport_change": false, "technical_stops": 0, "throw_away_ticketing": false, "hidden_city_ticketing": false, "virtual_interlining": false, "local_arrival": "2023-04-06T21:15:00.000Z", "utc_arrival": "2023-04-06T19:15:00.000Z", "local_departure": "2023-04-06T17:45:00.000Z", "utc_departure": "2023-04-06T15:45:00.000Z"}], "_results": 289, "search_params": {"flyFrom_type": "airport", "to_type": "airport", "seats": {"passengers": 2, "adults": 2, "children": 0, "infants": 0}}, "all_stopover_airports": [], "sort_version": 0}'

In [2]:
type(x)

str

In [3]:
import json

In [4]:
dictData= json.loads(x)

In [5]:
dictData

{'search_id': '56bd9ab9-36cb-f3b8-d6c0-0caca2accc79',
 'currency': 'HUF',
 'fx_rate': 382.006519,
 'data': [{'id': '0b770a224c4100007151a3a5_0|0a220b774c450000a94cee25_0',
   'flyFrom': 'BUD',
   'flyTo': 'MAD',
   'cityFrom': 'Budapest',
   'cityCodeFrom': 'BUD',
   'cityTo': 'Madrid',
   'cityCodeTo': 'MAD',
   'countryFrom': {'code': 'HU', 'name': 'Hungary'},
   'countryTo': {'code': 'ES', 'name': 'Spain'},
   'nightsInDest': 4,
   'quality': 536.654031,
   'distance': 1975.87,
   'duration': {'departure': 12000, 'return': 11400, 'total': 23400},
   'price': 146940.4926,
   'conversion': {'EUR': 384.654411, 'HUF': 146940.4926},
   'fare': {'adults': 73470.25, 'children': 73470.25, 'infants': 73470.25},
   'bags_price': {'1': 71.75, '2': 143.318},
   'baglimit': {'hand_height': 40,
    'hand_length': 55,
    'hand_weight': 10,
    'hand_width': 20,
    'hold_dimensions_sum': 319,
    'hold_height': 119,
    'hold_length': 119,
    'hold_weight': 20,
    'hold_width': 81,
    'persona

In [8]:
flight_result = FlightResultModel.from_dict(dictData)

In [9]:
flight_result

FlightResultModel(search_id=UUID('56bd9ab9-36cb-f3b8-d6c0-0caca2accc79'), currency='HUF', fx_rate=382.006519, data=[Datum(id='0b770a224c4100007151a3a5_0|0a220b774c450000a94cee25_0', fly_from='BUD', fly_to='MAD', city_from='Budapest', city_code_from='BUD', city_to='Madrid', city_code_to='MAD', country_from=Country(code='HU', name='Hungary'), country_to=Country(code='ES', name='Spain'), nights_in_dest=4, quality=536.654031, distance=1975.87, duration=Duration(departure=12000, duration_return=11400, total=23400), price=146940.4926, conversion=Conversion(eur=384.654411, huf=146940.4926), fare=Seats(adults=73470.25, children=73470.25, infants=73470.25, passengers=None), bags_price={'1': 71.75, '2': 143.318}, baglimit={'hand_height': 40, 'hand_length': 55, 'hand_weight': 10, 'hand_width': 20, 'hold_dimensions_sum': 319, 'hold_height': 119, 'hold_length': 119, 'hold_weight': 20, 'hold_width': 81, 'personal_item_height': 25, 'personal_item_length': 40, 'personal_item_weight': 10, 'personal_ite